# 21_2 Descriptive Analysis - Time Spans

Let us now take a closer look on the characterisitcs of our aggregrated data.

In [1]:
# import libraries
import pandas as pd
import numpy as np
import sklearn
from datetime import datetime
import os
import geopandas as gpd
import matplotlib.pyplot as plt
import folium
import shapely
import hashlib
import holidays
from shapely import Point, wkt
import scipy.stats
import seaborn as sns

## Load and prepare data

In [2]:
data_month_double = '07'

In [3]:
# read final data
data = pd.read_csv("../Data/20_Final_Data.csv")

/tmp/ipykernel_2575952/974816303.py:2: DtypeWarning: Columns (28) have mixed types. Specify dtype option on import or set low_memory=False.
  data = pd.read_csv("../../../20_Final_Data_NEW_TEST.csv")


In [4]:
tier = pd.read_parquet("../Data/12_tier_part2.parquet")
next = pd.read_parquet("../Data/15_nextbike_part2.parquet")

In [5]:
tier['trip_duration_seconds'] = tier['trip_duration'].dt.total_seconds()
next['trip_duration_seconds'] = next['trip_duration'].dt.total_seconds()

In [6]:
# transform geometry
data['station_point'] = data['station_point'].apply(wkt.loads)

In [7]:
data['buffer_zone'] = shapely.wkt.loads(data['buffer_zone'])

In [8]:
data = gpd.GeoDataFrame(data, geometry='station_point')

In [9]:
data = data.loc[:, ~data.columns.str.contains('Unnamed')]

In [10]:
#data.drop(columns=['Unnamed: 0', 'Unnamed: 0.1', 'Unnamed: 0.2'], inplace=True)

In [11]:
data['actual_arrival_time'] = pd.to_datetime(data['actual_arrival_time'])
data['actual_departure_time'] = pd.to_datetime(data['actual_departure_time'])
data['scheduled_arrival_time'] = pd.to_datetime(data['scheduled_arrival_time'])
data['scheduled_departure_time'] = pd.to_datetime(data['scheduled_departure_time'])

In [12]:
data = gpd.GeoDataFrame(data, geometry='buffer_zone')

In [13]:
data.info()

<class 'geopandas.geodataframe.GeoDataFrame'>
RangeIndex: 2564861 entries, 0 to 2564860
Data columns (total 56 columns):
 #   Column                               Dtype         
---  ------                               -----         
 0   route_id                             int64         
 1   agency_id                            int64         
 2   route_short_name                     object        
 3   route_type                           int64         
 4   route_type_name                      object        
 5   agency_name                          object        
 6   service_id                           int64         
 7   trip_id                              object        
 8   trip_headsign                        object        
 9   direction_id                         int64         
 10  shape_id                             int64         
 11  stop_id                              int64         
 12  actual_arrival_time                  datetime64[ns]
 13  actual_departure_ti

In [14]:
data['date'] = pd.to_datetime(data['date'])

In [15]:
data['arrival_delay'] = pd.to_timedelta(data['arrival_delay'])
data['departure_delay'] = pd.to_timedelta(data['departure_delay'])

In [16]:
data['arrival_delay_float'] = data['arrival_delay'].astype(str)
data['arrival_delay_float'] = data['arrival_delay_float'].str.split(' ', n=2).str[-1]
data['arrival_delay_float'] = data['arrival_delay_float'].astype(str)
data['arrival_delay_float'] = pd.to_timedelta(data['arrival_delay_float'])
data['arrival_delay_float'] = pd.to_timedelta(data['arrival_delay_float']).dt.total_seconds() / 60

In [17]:
data['departure_delay_float'] = data['departure_delay'].astype(str)
data['departure_delay_float'] = data['departure_delay_float'].str.split(' ', n=2).str[-1]
data['departure_delay_float'] = data['departure_delay_float'].astype(str)
data['departure_delay_float'] = pd.to_timedelta(data['departure_delay_float'])
data['departure_delay_float'] = pd.to_timedelta(data['departure_delay_float']).dt.total_seconds() / 60

In [18]:
#NEW FEATURES
data['delay_category'] = data['arrival_delay'].apply(lambda x: 1 if x > pd.Timedelta(0) else 0 if x == pd.Timedelta(0) else -1)
data['cancelled_trip'] = np.where((data['scheduled_arrival_time'].notna() & data['actual_arrival_time'].isna() & data['scheduled_departure_time'].notna() & data['actual_departure_time'].isna()), 1, 0)

## Data Description

### Definition of functions

In [19]:
def calc_stats(data, column_name):

    #generated by Copilot

    rows = len(data.index)

    sum = data[column_name].sum()

#Central Tendency

    # Calculate mean (average)
    mean = data[column_name].mean()
    # Calculate median (middle value)
    median = data[column_name].median()
    # Calculate mode (most frequent value)
    mode = data[column_name].mode()
    #calc maximum
    max = data[column_name].max()
    #calc minimum
    min = data[column_name].min()

    # Calculate range
    data_range = data[column_name].max() - data[column_name].min()
    # Calculate coefficient of variation of range
    cvr = data_range / mean
    # Calculate coefficient of variation of mean
    cvm = mean / mean
    # Calculate coefficient of variation of median
    cvmed = median / mean
    # Calculate coefficient of variation of mode
    cvmode = mode / mean
    # Calculate coefficient of variation of standard deviation
   

# Variability
# Measure of how spread out the values in a data set are
    
    # Calculate standard deviation (average amount of variability in a dataset; tells how far each score lies from the mean; the larger the standard deviation, the more variable the data)
    std_dev = data[column_name].std()
    # Calculate variance (average squared deviation from the mean; square of standard deviation; units of varriance are much larger than those of a typical value in the dataset)
    variance = data[column_name].var()
    # Calculate coefficient of variation
    cv = std_dev / mean # standard deviation divided by the mean; measures the relative variability of a dataset; allows comparison of variability of datasets with different units of measurement
    # Calculate 25th percentile
    percentile_25 = data[column_name].quantile(0.25)
    # Calculate 75th percentile
    percentile_75 = data[column_name].quantile(0.75)
    # Calculate interquartile range
    iqr = percentile_75 - percentile_25 # difference between the 75th and 25th percentiles; measures the spread of the middle 50% of values in a dataset
    # Calculate coefficient of quartile deviation
    qd = iqr / (percentile_75 + percentile_25)
    # Calculate coefficient of variation of coefficient of variation
    cvcv = std_dev / mean
    # Calculate coefficient of variation of coefficient of quartile deviation
    cvqd = iqr / (percentile_75 + percentile_25)
    # Calculate coefficient of variation of range

#Measure of Shape

    # Calculate skewness - measure of how much the probability distribution of a random variable deviates from the normal distribution
    skewness = data[column_name].skew()
    
    # Calculate kurtosis
    kurtosis = data[column_name].kurtosis()

    # Calculate coefficient of skewness
    cs = skewness / std_dev
    # Calculate coefficient of kurtosis
    ck = kurtosis / std_dev
    # Calculate coefficient of variation of skewness
    cvs = skewness / std_dev
    # Calculate coefficient of variation of kurtosis
    cvk = kurtosis / std_dev
    # Calculate coefficient of variation of coefficient of skewness
    cvcs = skewness / std_dev
    # Calculate coefficient of variation of coefficient of kurtosis
    cvck = kurtosis / std_dev
    
    
    
    #return "column: " + str(column_name), "mean: " + str(mean), "median: " + str(median), "mode: " + str(mode), "std_dev: " + str(std_dev), "variance: " + str(variance), "skewness: "+ str(skewness), "kurtosis: " + str(kurtosis), "percentile_25: "+ str(percentile_25), "percentile_75: "+ str(percentile_75), "iqr: " + str(iqr), "range: "+ str(data_range), "cv"+ str(cv), "qd: "+str(qd), "cs: "+ str(cs), "ck: " + str(ck), "csv: "+ str(cvs), "cvk: "+ str(cvk), "cvcs: "+ str(cvcs), "cvck: " +str(cvck), "cvcv: "+ str(cvcv), "cvqd: "+ str (cvqd), "cvr: "+ str(cvr), "cvm: " + str(cvm), "cvmed: " + str(cvmed), "cvmode: "+ str(cvmode)

    return pd.DataFrame({'column': [column_name],
                         'rows': [rows],
                         'sum': [sum],
                         'mean': [mean],
                         'median': [median],
                         'mode': [mode],
                         'max': [max],
                         'min': [min],
                         'std_dev': [std_dev],
                         'variance': [variance],
                         'skewness': [skewness],
                         'kurtosis': [kurtosis],
                         'percentile_25': [percentile_25],
                         'percentile_75': [percentile_75],
                         'iqr': [iqr],
                         'range': [data_range],
                         'cv': [cv],
                         'qd': [qd],
                         'cs': [cs],
                         'ck': [ck],
                         'cvs': [cvs],
                         'cvk': [cvk],
                         'cvcs': [cvcs],
                         'cvck': [cvck],
                         'cvcv': [cvcv],
                         'cvqd': [cvqd],
                         'cvr': [cvr],
                         'cvm': [cvm],
                         'cvmed': [cvmed],
                         'cvmode': [cvmode]}).T

In [20]:
# create a shorter dataframe with most interesting columns - for better overview
def show_short_df(dataframe):
    delay_short = dataframe[['route_id', 'trip_id', 'stop_id', 'stop_name', 'scheduled_arrival_time', 'actual_arrival_time', 'scheduled_departure_time', 'actual_departure_time', 'arrival_delay', 'departure_delay', 'tier_trips_count', 'tier_trips_end_at_station_count', 'nextbike_trips_count', 'nextbike_trips_end_at_station_count', 'buffer_zone', 'arrival_delay_float', 'departure_delay_float']]
    return delay_short

In [21]:
# transform geometry
point_start = gpd.GeoDataFrame(geometry=gpd.GeoSeries.from_wkb(tier["start_location"], crs=4326))
point_end = gpd.GeoDataFrame(geometry=gpd.GeoSeries.from_wkb(tier["end_location"], crs=4326))
# drop geometry columns in wrong format
tier = tier.drop(columns=["start_location", "end_location"])
# replace geometry columns with correct format
tier['start_location'] = point_start
tier['end_location'] = point_end

In [22]:
# get the data from the tier / nextbike dataset
def check_micromobility_datasets(type, data):
    
    if type == 'tier':

        return_data = tier.copy()
        return_data = return_data.iloc[0:0] # empty dataframe

        for item in data['tier_trips_id'].str.split(' ').explode().dropna():   # iterate over all tier ids in the dataframe
            
            id = tier[tier['tier_trips_id'] == int(float(item))]   # get the rows with the specific id
            return_data = pd.concat([return_data, id])  # add the rows to the return dataframe

            return_data.drop_duplicates(inplace=True)
            
    if type == 'next':

        return_data = next.copy()
        return_data = return_data.iloc[0:0] # empty dataframe

        for item in data['nextbike_trips_id'].str.split(' ').explode().dropna():   # iterate over all nextbike ids in the dataframe
            
            id = next[next['nextbike_trips_id'] == int(float(item))]  # get the rows with the specific id
            return_data = pd.concat([return_data, id]) # add the rows to the return dataframe

            return_data.drop_duplicates(inplace=True)

    return return_data

In [23]:
def get_station_to_station(data):
    t = check_micromobility_datasets('tier', data)
    n = check_micromobility_datasets('nextbike', data)

    t = t[t['end_stop_id'].notna() & t['start_stop_id'].notna()]
    n = n[n['end_stop_id'].notna() & n['start_stop_id'].notna()]
    
    return t, n

In [24]:
# map the start and end locations of the trips on a map and connect them with a line

def map_buffer_zones(dataset):
    
    micromobility_data = check_micromobility_datasets('tier', dataset)
    
    # Create a folium map object
    m = folium.Map(location=[50.73743, 7.09821], zoom_start=12)

    # Iterate over each row in the micromobility data
    for index, row in micromobility_data.iterrows():
        # Get the start and end locations
        start_location = row['start_location']
        end_location = row['end_location']
        
        # Get the start and end stop names
        start_stop_name = row['start_stop_name']
        end_stop_name = row['end_stop_name']
        # Add markers for the start and end locations
        folium.Marker(location=[start_location.y, start_location.x], popup=start_stop_name).add_to(m)
        folium.Marker(location=[end_location.y, end_location.x], popup=end_stop_name).add_to(m)
        # Create a line connecting the start and end locations
        folium.PolyLine(locations=[[start_location.y, start_location.x], [end_location.y, end_location.x]], color='blue').add_to(m)
        
    # Display the map
    return m

In [25]:
def get_stats(data, var):
    
    df = pd.DataFrame()

    for i in var:
        df = pd.concat([df, calc_stats(data, i)], axis=1)

    df.columns = df.iloc[0]
    df = df[1:]
    
    return df

## Create Delay, No_Delay, and Nan-Delay Datasets

In [26]:
delay = data[data['departure_delay'] > pd.Timedelta(0)]


In [27]:
#no_delay = data[data['arrival_delay'] == pd.Timedelta(0)]
no_delay = data[
    (data['departure_delay'] == pd.Timedelta(0)) | 
    (data['scheduled_arrival_time'].notna() & 
     data['actual_arrival_time'].isna() & 
     data['scheduled_departure_time'].notna() & 
     data['actual_departure_time'].notna())
]

In [28]:
#nan_delay = data[data['arrival_delay'].isna()]
nan_delay = data[data['scheduled_arrival_time'].notna() & data['actual_arrival_time'].isna() & data['scheduled_departure_time'].notna() & data['actual_departure_time'].isna()]
#nan_delay = data[data['arrival_delay'].isna()]
nan_delay

route_id  agency_id route_short_name  route_type route_type_name  \
41            551          8              551           3             Bus   
42            551          8              551           3             Bus   
43            551          8              551           3             Bus   
44            551          8              551           3             Bus   
45            551          8              551           3             Bus   
...           ...        ...              ...         ...             ...   
2564854       689          6               N9           3             Bus   
2564856       689          6               N9           3             Bus   
2564857       689          6               N9           3             Bus   
2564858       689          6               N9           3             Bus   
2564860       689          6               N9           3             Bus   

                                      agency_name  service_id  \
41       RSVG Rhein-Sieg-Verkehrsgesellschaft mbH         125   
42       RSVG Rhein-Sieg-Verkehrsgesellschaft mbH         125   
43       RSVG Rhein-Sieg-Verkehrsgesellschaft mbH         125   
44       RSVG Rhein-Sieg-Verkehrsgesellschaft mbH         125   
45       RSVG Rhein-Sieg-Verkehrsgesellschaft mbH         125   
...                                           ...         ...   
2564854         SWB Stadtwerke Bonn Verkehrs GmbH          43   
2564856         SWB Stadtwerke Bonn Verkehrs GmbH          43   
2564857         SWB Stadtwerke Bonn Verkehrs GmbH          43   
2564858         SWB Stadtwerke Bonn Verkehrs GmbH          43   
2564860         SWB Stadtwerke Bonn Verkehrs GmbH          43   

                                                   trip_id trip_headsign  \
41       255-551-008-2071.2.22:033200-34-157_C0741D60-B...      Bonn Hbf   
42       159-551-008-687.2.36:044000-33-157_FAA787CB-18...  Troisdorf Bf   
43       159-551-008-687.2.36:044000-33-157_FAA787CB-18...  Troisdorf Bf   
44       159-551-008-687.2.36:044000-33-157_FAA787CB-18...  Troisdorf Bf   
45       159-551-008-687.2.36:044000-33-157_FAA787CB-18...  Troisdorf Bf   
...                                                    ...           ...   
2564854  6890005-689-006-687.2.34:263500-53-1_2AFE8F0F-...      Bonn Hbf   
2564856  6890005-689-006-687.2.34:263500-53-1_2AFE8F0F-...      Bonn Hbf   
2564857  6890005-689-006-687.2.34:263500-53-1_2AFE8F0F-...      Bonn Hbf   
2564858  6890005-689-006-687.2.34:263500-53-1_2AFE8F0F-...      Bonn Hbf   
2564860  6890005-689-006-687.2.34:263500-53-1_2AFE8F0F-...      Bonn Hbf   

         direction_id  ...  delay_span  arrival_delay_span weather_int  \
41                  1  ...           0                   0           0   
42                  0  ...           0                   0           0   
43                  0  ...           0                   0           0   
44                  0  ...           0                   0           0   
45                  0  ...           0                   0           0   
...               ...  ...         ...                 ...         ...   
2564854             0  ...           0                   0           1   
2564856             0  ...           0                   0           1   
2564857             0  ...           0                   0           1   
2564858             0  ...           0                   0           1   
2564860             0  ...           0                   0           1   

        time_span_arrival  time_span_int_arrival  weekend time_span  \
41                      0                      0        1         0   
42                      0                      0        1         0   
43                      0                      0        1         0   
44                      0                      0        1         0   
45                      0                      0        1         0   
...                   ...                    ...      ...       ...   
2564

### Time

Micromobilty usage depends on time and weekday. The literature finds differences beteen work commuting times and leisure activities. 

#### Morning Rush

In [29]:
morning_rush_delay = delay[(delay['scheduled_arrival_time'].dt.hour >= 6) & (delay['scheduled_arrival_time'].dt.hour <= 9)]
morning_rush_delay

route_id  agency_id route_short_name  route_type route_type_name  \
2651          606          6              606           3             Bus   
2652          602          6              602           3             Bus   
2654          611          6              611           3             Bus   
2655          600          6              600           3             Bus   
2661          600          6              600           3             Bus   
...           ...        ...              ...         ...             ...   
2494915       633          6              633           3             Bus   
2494917       600          6              600           3             Bus   
2494918       600          6              600           3             Bus   
2494919       601          6              601           3             Bus   
2494925       610          6              610           3             Bus   

                               agency_name  service_id  \
2651     SWB Stadtwerke Bonn Verkehrs GmbH          43   
2652     SWB Stadtwerke Bonn Verkehrs GmbH          43   
2654     SWB Stadtwerke Bonn Verkehrs GmbH         130   
2655     SWB Stadtwerke Bonn Verkehrs GmbH         130   
2661     SWB Stadtwerke Bonn Verkehrs GmbH         130   
...                                    ...         ...   
2494915  SWB Stadtwerke Bonn Verkehrs GmbH          64   
2494917  SWB Stadtwerke Bonn Verkehrs GmbH          64   
2494918  SWB Stadtwerke Bonn Verkehrs GmbH          64   
2494919  SWB Stadtwerke Bonn Verkehrs GmbH          64   
2494925  SWB Stadtwerke Bonn Verkehrs GmbH          64   

                                                   trip_id  \
2651     6060003-606-006-1357.2.21:053800-42-1_4E8CA248...   
2652     6020006-602-006-9478.2.22:055600-39-1_812F7A36...   
2654     6110147-611-006-1723.2.21:055000-60-1_39D7C4D7...   
2655     6000317-600-006-687.2.24:054500-16-1_7F8D7B79-...   
2661     6000317-600-006-687.2.24:054500-16-1_7F8D7B79-...   
...                                                    ...   
2494915  6330028-633-006-1584.2.24:094300-24-1_5B1B51F9...   
2494917  6000027-600-006-1308.2.21:092500-36-1_B8848C0F...   
2494918  6000028-600-006-8813.2.22:095900-32-1_53EFFD6B...   
2494919  6010051-601-006-1293.2.21:085900-46-1_5C215E86...   
2494925  6100057-610-006-1756.2.21:092600-54-1_FE6EB802...   

                trip_headsign  direction_id  ...  delay_span  \
2651               Ramersdorf             0  ...         0-5   
2652                   Waldau             1  ...         0-5   
2654     Lessenich Sportplatz             0  ...         0-5   
2655                Kranenweg             0  ...         0-5   
2661                Kranenweg             0  ...         0-5   
...                       ...           ...  ...         ...   
2494915      Endenich Nord Bf             1  ...         0-5   
2494917             Kranenweg             0  ...         0-5   
2494918   Ippendorf Altenheim             1  ...         0-5   
2494919    Agnetendorfer Str.             0  ...         0-5   
2494925           Duisdorf Bf             0  ...         0-5   

         arrival_delay_span weather_int time_span_arrival  \
2651                      0           0      morning rush   
2652                      0           0      morning rush   
2654                      0           0      morning rush   
2655                      0           0      morning rush   
2661                      0           0      morning rush   
...                     ...         ...               ...   
2494915                   0           1      morning rush   
2494917                   0           1      morning rush   
2494918                   0           1      morning rush   
2494919                   0           1      morning rush   
2494925                   0           1      morning rush   

         time_span_int_arrival  weekend     time_span time_span_int  \
2651                         1        2  morning rush             1  

In [30]:
get_stats(morning_rush_delay, ['tier_trips_count', 'tier_trips_end_at_station_count', 'nextbike_trips_count', 'nextbike_trips_end_at_station_count', 'current_temp', 'current_precipitation_volume'])

/tmp/ipykernel_2575952/41814695.py:51: RuntimeWarning: invalid value encountered in scalar divide
  qd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:55: RuntimeWarning: invalid value encountered in scalar divide
  cvqd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:51: RuntimeWarning: invalid value encountered in scalar divide
  qd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:55: RuntimeWarning: invalid value encountered in scalar divide
  cvqd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:51: RuntimeWarning: invalid value encountered in scalar divide
  qd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:55: RuntimeWarning: invalid value encountered in scalar divide
  cvqd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:51: RuntimeWarning: invalid value encountered in scalar divide
  qd = iqr / (percentile_75 + percenti

column                                        tier_trips_count  \
rows                                                    188742   
sum                                                       1841   
mean                                                  0.009754   
median                                                     0.0   
mode               0    0
Name: tier_trips_count, dtype: int64   
max                                                          6   
min                                                          0   
std_dev                                               0.101776   
variance                                              0.010358   
skewness                                             11.738289   
kurtosis                                             192.98451   
percentile_25                                              0.0   
percentile_75                                              0.0   
iqr                                                        0.0   
range                                                        6   
cv                                                   10.434215   
qd                                                         NaN   
cs                                                  115.334643   
ck                                                 1896.170757   
cvs                                                 115.334643   
cvk                                                1896.170757   
cvcs                                                115.334643   
cvck                                               1896.170757   
cvcv                                                 10.434215   
cvqd                                                       NaN   
cvr                                                 615.128734   
cvm                                                        1.0   
cvmed                                                      0.0   
cvmode         0    0.0
Name: tier_trips_count, dtype: float64   

column                           tier_trips_end_at_station_count  \
rows                                                      188742   
sum                                                         1497   
mean                                                    0.007931   
median                                                       0.0   
mode           0    0
Name: tier_trips_end_at_station_count, ...   
max                                                            6   
min                                                            0   
std_dev                                                 0.092162   
variance                                                0.008494   
skewness                                               13.325357   
kurtosis                                              258.154778   
percentile_25                                                0.0   
percentile_75                                                0.0   
iqr                                                          0.0   
range                                                          6   
cv                                                      11.61977   
qd                                                           NaN   
cs                                                    144.586612   
ck                                                   2801.104959   
cvs                                                   144.586612   
cvk                                                  2801.104959   
cvcs                                                  144.586612   
cvck                                                 2801.104959   
cvcv                                                    11.61977   
cvqd                                                         NaN   
cvr                                                   756.480962   
cvm                                                          1.0   
cvmed                                                        0.0   
cvmode         0    0.0
Name: tier_trips_end_at

In [31]:
morning_rush_delay_tier = check_micromobility_datasets('tier', morning_rush_delay)

In [32]:
morning_rush_delay_tier.describe()

tier_trips_id          tier_trips_start_time  \
count   1.180000e+03                           1180   
mean    7.964934e+08  2023-07-14 16:38:28.220338944   
min     7.822651e+08            2023-07-01 06:25:00   
25%     7.823741e+08            2023-07-07 08:02:30   
50%     7.824542e+08            2023-07-13 07:30:00   
75%     8.087219e+08            2023-07-21 09:00:00   
max     8.323095e+08            2023-07-31 09:50:00   
std     1.609937e+07                            NaN   

                 tier_trips_end_time              trip_duration  \
count                           1180                       1180   
mean   2023-07-14 16:51:30.762711808  0 days 00:13:02.542372881   
min              2023-07-01 06:30:00            0 days 00:05:00   
25%              2023-07-07 08:12:30            0 days 00:10:00   
50%              2023-07-13 07:37:30            0 days 00:10:00   
75%              2023-07-21 09:06:15            0 days 00:15:00   
max              2023-07-31 10:10:00            0 days 01:40:00   
std                              NaN  0 days 00:07:52.213825792   

       trip_distance_kilometers  trip_distance_meters  start_stop_id  \
count               1180.000000           1180.000000     828.000000   
mean                   1.649874           1649.873724    1519.801932   
min                    0.100712            100.712421      43.000000   
25%                    0.748799            748.799184    1106.000000   
50%                    1.325392           1325.392316    1145.500000   
75%                    2.168419           2168.418704    1292.000000   
max                    8.135201           8135.200888    9780.000000   
std                    1.275224           1275.224148    1580.175252   

       end_stop_id  trip_duration_seconds  
count   670.000000            1180.000000  
mean   1219.844776             782.542373  
min      43.000000             300.000000  
25%     698.000000             600.000000  
50%    1115.000000             600.000000  
75%    1224.000000             900.000000  
max    9780.000000            6000.000000  
std    1079.455096             472.213826

In [33]:
get_stats(morning_rush_delay_tier, ['trip_duration_seconds', 'trip_distance_kilometers'])

column                                     trip_duration_seconds  \
rows                                                        1180   
sum                                                     923400.0   
mean                                                  782.542373   
median                                                     600.0   
mode           0    600.0
Name: trip_duration_seconds, dtype:...   
max                                                       6000.0   
min                                                        300.0   
std_dev                                               472.213826   
variance                                            222985.89727   
skewness                                                4.113108   
kurtosis                                               32.526141   
percentile_25                                              600.0   
percentile_75                                              900.0   
iqr                                                        300.0   
range                                                     5700.0   
cv                                                      0.603435   
qd                                                           0.2   
cs                                                       0.00871   
ck                                                       0.06888   
cvs                                                      0.00871   
cvk                                                      0.06888   
cvcs                                                     0.00871   
cvck                                                     0.06888   
cvcv                                                    0.603435   
cvqd                                                         0.2   
cvr                                                     7.283951   
cvm                                                          1.0   
cvmed                                                   0.766732   
cvmode         0    0.766732
Name: trip_duration_seconds, dty...   

column                                  trip_distance_kilometers  
rows                                                        1180  
sum                                                  1946.850994  
mean                                                    1.649874  
median                                                  1.325392  
mode           0       0.100712
1       0.101362
2       0.10...  
max                                                     8.135201  
min                                                     0.100712  
std_dev                                                 1.275224  
variance                                                1.626197  
skewness                                                1.621782  
kurtosis                                                3.416849  
percentile_25                                           0.748799  
percentile_75                                           2.168419  
iqr                                                      1.41962  
range                                                   8.034488  
cv                                                      0.772922  
qd                                                      0.486635  
cs                                                      1.271762  
ck                                                      2.679411  
cvs                                                     1.271762  
cvk                                                     2.679411  
cvcs                                                    1.271762  
cvck                                                    2.679411  
cvcv                                                    0.772922  
cvqd                                                    0.486635  
cvr                                                      4.86976  
cvm                                                          1.0  
cvmed                                                    0.80333  
cvmode         0

In [34]:
# get entries where trips start and end at station
morning_rush_delay_tier_station_station = morning_rush_delay_tier[morning_rush_delay_tier['end_stop_id'].notna() & morning_rush_delay_tier['start_stop_id'].notna()]
morning_rush_delay_tier_station_station

tier_trips_id tier_trips_start_time tier_trips_end_time vehicle type  \
3234236      782413798   2023-07-01 06:40:00 2023-07-01 06:45:00    e-scooter   
3164060      782350073   2023-07-01 07:10:00 2023-07-01 07:15:00    e-scooter   
3109531      782329093   2023-07-01 07:25:00 2023-07-01 07:45:00    e-scooter   
2999342      782294477   2023-07-01 07:30:00 2023-07-01 07:35:00    e-scooter   
2968238      782284561   2023-07-01 07:50:00 2023-07-01 08:00:00    e-scooter   
...                ...                   ...                 ...          ...   
3473714      832254380   2023-07-31 08:45:00 2023-07-31 08:55:00    e-scooter   
3325477      832124843   2023-07-31 09:20:00 2023-07-31 09:30:00    e-scooter   
3330682      832128386   2023-07-31 09:40:00 2023-07-31 09:55:00    e-scooter   
3416876      832199842   2023-07-31 09:40:00 2023-07-31 09:50:00    e-scooter   
3453395      832234899   2023-07-31 09:50:00 2023-07-31 10:05:00    e-scooter   

          trip_duration  trip_distance_kilometers  trip_distance_meters  \
3234236 0 days 00:05:00                  0.844529            844.529088   
3164060 0 days 00:05:00                  0.941159            941.158971   
3109531 0 days 00:20:00                  1.863754           1863.753840   
2999342 0 days 00:05:00                  0.458642            458.641594   
2968238 0 days 00:10:00                  0.826336            826.335632   
...                 ...                       ...                   ...   
3473714 0 days 00:10:00                  0.211118            211.118491   
3325477 0 days 00:10:00                  0.920274            920.273564   
3330682 0 days 00:15:00                  1.125842           1125.841563   
3416876 0 days 00:10:00                  3.058432           3058.432358   
3453395 0 days 00:15:00                  2.005188           2005.187551   

         start_stop_id                            start_stop_name  \
3234236         1131.0                             Bonn Weberstr.   
3164060         1182.0                         Bonn Chlodwigplatz   
3109531         1102.0                         Bonn Friedensplatz   
2999342         2667.0  Bonn Brüdergasse/Bertha-Von-Suttner-Platz   
2968238         1620.0                        Bonn Max-Bruch-Str.   
...                ...                                        ...   
3473714         1110.0                         Bonn Wilhelmsplatz   
3325477         1525.0                         Bonn Geislar Mitte   
3330682         1102.0                         Bonn Friedensplatz   
3416876         1115.0  Bonn Bertha-Von-Suttner-Pl./Beethovenhaus   
3453395         1115.0  Bonn Bertha-Von-Suttner-Pl./Beethovenhaus   

                                         start_buffer_zone  end_stop_id  \
3234236  801621     POLYGON ((7.157885983913106 50.7227...        687.0   
3164060  801621     POLYGON ((7.157885983913106 50.7227...        688.0   
3109531  801621     POLYGON ((7.157885983913106 50.7227...       1221.0   
2999342  801621     POLYGON ((7.157885983913106 50.7227...       1103.0   
2968238  801621     POLYGON ((7.157885983913106 50.7227...       1234.0   
...                                                    ...          ...   
3473714  801621     POLYGON ((7.157885983913106 50.7227...       1110.0   
3325477  801621     POLYGON ((7.157885983913106 50.7227...       1523.0   
3330682  801621     POLYGON ((7.157885983913106 50.7227...       1175.0   
3416876  801621     POLYGON ((7.157885983913106 50.7227...       1540.0   
3453395  801621     POLYGON ((7.157885983913106 50.7227...       1500.0   

                      end_stop_name  \
3234236                    Bonn Hbf   
3164060                   Bonn West   
3109531           Bonn Kaufmannstr.   
2999342                  Bonn Markt   
2968238       Bonn Am Klostergarten   
...                             ...   
3473714          Bonn Wilhelmsplatz   
3325477         Bonn Vilich Kloster   
3330682             Bonn Lvr-Klinik   
3416876        

In [35]:
morning_rush_delay_tier_station_station.describe()

tier_trips_id          tier_trips_start_time  \
count   5.370000e+02                            537   
mean    7.961077e+08  2023-07-14 06:56:07.039106048   
min     7.822651e+08            2023-07-01 06:40:00   
25%     7.823646e+08            2023-07-07 06:25:00   
50%     7.824477e+08            2023-07-12 07:50:00   
75%     8.087265e+08            2023-07-21 08:55:00   
max     8.323095e+08            2023-07-31 09:50:00   
std     1.655534e+07                            NaN   

                 tier_trips_end_time              trip_duration  \
count                            537                        537   
mean   2023-07-14 07:08:16.089385472  0 days 00:12:09.050279329   
min              2023-07-01 06:45:00            0 days 00:05:00   
25%              2023-07-07 06:40:00            0 days 00:10:00   
50%              2023-07-12 07:55:00            0 days 00:10:00   
75%              2023-07-21 09:00:00            0 days 00:15:00   
max              2023-07-31 10:05:00            0 days 01:40:00   
std                              NaN  0 days 00:08:24.470343718   

       trip_distance_kilometers  trip_distance_meters  start_stop_id  \
count                537.000000            537.000000     537.000000   
mean                   1.297397           1297.396641    1426.564246   
min                    0.101362            101.362372     161.000000   
25%                    0.643317            643.317394    1106.000000   
50%                    1.091158           1091.157710    1145.000000   
75%                    1.813185           1813.185057    1240.000000   
max                    6.209313           6209.312760    9703.000000   
std                    0.936345            936.344582    1358.930227   

       end_stop_id  trip_duration_seconds  
count   537.000000             537.000000  
mean   1244.713222             729.050279  
min      43.000000             300.000000  
25%    1102.000000             600.000000  
50%    1115.000000             600.000000  
75%    1224.000000             900.000000  
max    9780.000000            6000.000000  
std    1045.176379             504.470344

In [36]:
# get statistics for the tier trips that start and end at a station
get_stats(morning_rush_delay_tier_station_station, ['trip_duration_seconds', 'trip_distance_kilometers'])

column                                     trip_duration_seconds  \
rows                                                         537   
sum                                                     391500.0   
mean                                                  729.050279   
median                                                     600.0   
mode           0    600.0
Name: trip_duration_seconds, dtype:...   
max                                                       6000.0   
min                                                        300.0   
std_dev                                               504.470344   
variance                                           254490.327691   
skewness                                                5.958041   
kurtosis                                               52.536479   
percentile_25                                              600.0   
percentile_75                                              900.0   
iqr                                                        300.0   
range                                                     5700.0   
cv                                                      0.691955   
qd                                                           0.2   
cs                                                       0.01181   
ck                                                      0.104142   
cvs                                                      0.01181   
cvk                                                     0.104142   
cvcs                                                     0.01181   
cvck                                                    0.104142   
cvcv                                                    0.691955   
cvqd                                                         0.2   
cvr                                                     7.818391   
cvm                                                          1.0   
cvmed                                                   0.822989   
cvmode         0    0.822989
Name: trip_duration_seconds, dty...   

column                                  trip_distance_kilometers  
rows                                                         537  
sum                                                   696.701996  
mean                                                    1.297397  
median                                                  1.091158  
mode           0      0.101362
1      0.105554
2      0.10668...  
max                                                     6.209313  
min                                                     0.101362  
std_dev                                                 0.936345  
variance                                                0.876741  
skewness                                                1.498469  
kurtosis                                                3.523494  
percentile_25                                           0.643317  
percentile_75                                           1.813185  
iqr                                                     1.169868  
range                                                    6.10795  
cv                                                       0.72171  
qd                                                      0.476233  
cs                                                      1.600339  
ck                                                      3.763031  
cvs                                                     1.600339  
cvk                                                     3.763031  
cvcs                                                    1.600339  
cvck                                                    3.763031  
cvcv                                                     0.72171  
cvqd                                                    0.476233  
cvr                                                     4.707851  
cvm                                                          1.0  
cvmed                                                   0.841036  
cvmode         0

In [37]:
morning_rush_delay_next = check_micromobility_datasets('next', morning_rush_delay)

In [38]:
morning_rush_delay_next.describe()

nextbike_trips_id      nextbike_trips_start_time  \
count       3.578000e+03                           3578   
mean        3.793870e+07  2023-07-15 02:04:46.416993024   
min         3.771654e+07            2023-07-01 06:06:00   
25%         3.782777e+07            2023-07-07 09:06:00   
50%         3.794210e+07            2023-07-14 06:06:00   
75%         3.804716e+07            2023-07-21 08:13:30   
max         3.817162e+07            2023-07-31 10:01:00   
std         1.279113e+05                            NaN   

             nextbike_trips_end_time              trip_duration  \
count                           3578                       3578   
mean   2023-07-15 02:18:33.705980672  0 days 00:13:47.288988261   
min              2023-07-01 06:16:00            0 days 00:05:00   
25%              2023-07-07 09:16:00            0 days 00:10:00   
50%              2023-07-14 06:16:00            0 days 00:10:00   
75%              2023-07-21 08:24:45            0 days 00:15:00   
max              2023-07-31 10:46:00            0 days 01:35:00   
std                              NaN  0 days 00:08:06.964519406   

       trip_distance_kilometers  trip_distance_meters  start_stop_id  \
count               3578.000000           3578.000000    2664.000000   
mean                   1.701428           1701.428436    1355.129880   
min                    0.100317            100.317073      43.000000   
25%                    0.795715            795.714771    1103.000000   
50%                    1.361136           1361.135869    1150.000000   
75%                    2.225411           2225.410845    1224.000000   
max                   12.437610          12437.610008    9780.000000   
std                    1.317342           1317.341819    1331.651105   

       end_stop_id  trip_duration_seconds  
count  2196.000000            3578.000000  
mean   1129.138434             827.288988  
min      43.000000             300.000000  
25%     687.000000             600.000000  
50%    1131.000000             600.000000  
75%    1221.000000             900.000000  
max    9780.000000            5700.000000  
std     948.687153             486.964519

In [39]:
get_stats(morning_rush_delay_next, ['trip_duration_seconds', 'trip_distance_kilometers'])

column                                     trip_duration_seconds  \
rows                                                        3578   
sum                                                    2960040.0   
mean                                                  827.288988   
median                                                     600.0   
mode           0    600.0
Name: trip_duration_seconds, dtype:...   
max                                                       5700.0   
min                                                        300.0   
std_dev                                               486.964519   
variance                                           237134.443161   
skewness                                                3.840305   
kurtosis                                               26.562398   
percentile_25                                              600.0   
percentile_75                                              900.0   
iqr                                                        300.0   
range                                                     5400.0   
cv                                                      0.588627   
qd                                                           0.2   
cs                                                      0.007886   
ck                                                      0.054547   
cvs                                                     0.007886   
cvk                                                     0.054547   
cvcs                                                    0.007886   
cvck                                                    0.054547   
cvcv                                                    0.588627   
cvqd                                                         0.2   
cvr                                                     6.527344   
cvm                                                          1.0   
cvmed                                                    0.72526   
cvmode         0    0.72526
Name: trip_duration_seconds, dtyp...   

column                                  trip_distance_kilometers  
rows                                                        3578  
sum                                                  6087.710944  
mean                                                    1.701428  
median                                                  1.361136  
mode           0    0.834842
Name: trip_distance_kilometers, ...  
max                                                     12.43761  
min                                                     0.100317  
std_dev                                                 1.317342  
variance                                                1.735389  
skewness                                                1.927344  
kurtosis                                                6.134402  
percentile_25                                           0.795715  
percentile_75                                           2.225411  
iqr                                                     1.429696  
range                                                  12.337293  
cv                                                      0.774256  
qd                                                      0.473233  
cs                                                      1.463055  
ck                                                      4.656651  
cvs                                                     1.463055  
cvk                                                     4.656651  
cvcs                                                    1.463055  
cvck                                                    4.656651  
cvcv                                                    0.774256  
cvqd                                                    0.473233  
cvr                                                     7.251138  
cvm                                                          1.0  
cvmed                                                   0.799996  
cvmode         0

In [40]:
# get entries where trips start and end at station
morning_rush_delay_next_station_station = morning_rush_delay_next[morning_rush_delay_next['end_stop_id'].notna() & morning_rush_delay_next['start_stop_id'].notna()]
morning_rush_delay_next_station_station

nextbike_trips_id nextbike_trips_start_time nextbike_trips_end_time  \
1235649           37726317       2023-07-01 06:06:00     2023-07-01 06:21:00   
1267255           37827523       2023-07-01 06:06:00     2023-07-01 06:16:00   
1638081           37769500       2023-07-01 06:11:00     2023-07-01 06:21:00   
1267257           37827525       2023-07-01 06:31:00     2023-07-01 06:46:00   
1482863           37979215       2023-07-01 06:26:00     2023-07-01 06:36:00   
...                    ...                       ...                     ...   
1573919           38119861       2023-07-31 09:41:00     2023-07-31 09:51:00   
1619874           38153683       2023-07-31 09:41:00     2023-07-31 09:56:00   
1369123           37938091       2023-07-31 09:46:00     2023-07-31 09:56:00   
1419028           37963190       2023-07-31 09:51:00     2023-07-31 10:01:00   
1668246           37799665       2023-07-31 09:56:00     2023-07-31 10:11:00   

         nextbike_trips_start_at_station  nextbike_trips_end_at_station  \
1235649                            False                          False   
1267255                            False                          False   
1638081                            False                           True   
1267257                            False                          False   
1482863                            False                          False   
...                                  ...                            ...   
1573919                            False                          False   
1619874                            False                          False   
1369123                            False                          False   
1419028                            False                          False   
1668246                            False                          False   

        vehicle type   trip_duration  trip_distance_kilometers  \
1235649         bike 0 days 00:15:00                  2.055591   
1267255         bike 0 days 00:10:00                  1.000358   
1638081         bike 0 days 00:10:00                  0.914302   
1267257         bike 0 days 00:15:00                  1.548325   
1482863         bike 0 days 00:10:00                  1.099298   
...              ...             ...                       ...   
1573919         bike 0 days 00:10:00                  0.729241   
1619874         bike 0 days 00:15:00                  1.004462   
1369123         bike 0 days 00:10:00                  0.552211   
1419028         bike 0 days 00:10:00                  1.277644   
1668246         bike 0 days 00:15:00                  2.191948   

         trip_distance_meters  \
1235649           2055.591133   
1267255           1000.357907   
1638081            914.302426   
1267257           1548.325433   
1482863           1099.297704   
...                       ...   
1573919            729.241426   
1619874           1004.461946   
1369123            552.210742   
1419028           1277.644211   
1668246           2191.947986   

                                            start_location  \
1235649  b"\x01\x01\x00\x00\x00\xf0\xf8\xf6\xaeA_\x1c@\...   
1267255  b'\x01\x01\x00\x00\x00\xc0\x06D\x88+g\x1c@\xef...   
1638081  b'\x01\x01\x00\x00\x00\xc5V\xd0\xb4\xc4Z\x1c@\...   
1267257  b'\x01\x01\x00\x00\x00\xac:\xab\x05\xf6h\x1c@N...   
1482863      b'\x01\x01\x00\x00\x00+0du\xabg\x1c@fffff^I@'   
...                                                    ...   
1573919  b'\x01\x01\x00\x00\x00\x1e\x87\xc1\xfc\x15b\x1...   
1619874  b'\x01\x01\x00\x00\x00+/\xf9\x9f\xfc]\x1c@F\x9...   
1369123  b'\x01\x01\x00\x00\x00\xadK\x8d\xd0\xcfT\x1c@\...   
1419028  b'\x01\x01\x00\x00\x00qu\x00\xc4]]\x1c@F\xd3\x...   
1668246  b'\x01\x01\x00\x00\x00;U\xbeg$b\x1c@p\xcd\x1d\...   

                                              end_location  start_stop_id  \
1235649  b'\x01\x01\x00\x00\x00B\xd1<\x80En\x1c@\x84*5{...         1182.0   
1267255  b'\x01\x01\x00\x00\x00\x8f\x89\x94f\xf3h\x1c@f...

In [41]:
morning_rush_delay_next_station_station.describe()

nextbike_trips_id      nextbike_trips_start_time  \
count       1.788000e+03                           1788   
mean        3.794075e+07  2023-07-15 00:18:44.697986560   
min         3.771654e+07            2023-07-01 06:06:00   
25%         3.782814e+07            2023-07-07 09:36:00   
50%         3.794196e+07            2023-07-13 09:31:00   
75%         3.804858e+07            2023-07-21 07:38:30   
max         3.817162e+07            2023-07-31 09:56:00   
std         1.282322e+05                            NaN   

             nextbike_trips_end_time              trip_duration  \
count                           1788                       1788   
mean   2023-07-15 00:31:34.630872576  0 days 00:12:49.932885906   
min              2023-07-01 06:16:00            0 days 00:05:00   
25%              2023-07-07 09:46:00            0 days 00:10:00   
50%              2023-07-13 09:43:30            0 days 00:10:00   
75%              2023-07-21 07:52:15            0 days 00:15:00   
max              2023-07-31 10:46:00            0 days 01:25:00   
std                              NaN  0 days 00:06:27.608563376   

       trip_distance_kilometers  trip_distance_meters  start_stop_id  \
count               1788.000000           1788.000000    1788.000000   
mean                   1.468553           1468.553426    1374.473714   
min                    0.100317            100.317073     161.000000   
25%                    0.770483            770.483490    1103.000000   
50%                    1.248171           1248.171048    1145.000000   
75%                    1.928603           1928.603440    1223.000000   
max                    7.323831           7323.831097    9780.000000   
std                    1.023259           1023.259153    1351.899321   

       end_stop_id  trip_duration_seconds  
count  1788.000000            1788.000000  
mean   1148.562081             769.932886  
min      43.000000             300.000000  
25%     687.000000             600.000000  
50%    1131.000000             600.000000  
75%    1221.000000             900.000000  
max    9780.000000            5100.000000  
std     962.199953             387.608563

In [42]:
# get statistics for the tier trips that start and end at a station
get_stats(morning_rush_delay_next_station_station, ['trip_duration_seconds', 'trip_distance_kilometers'])

column                                     trip_duration_seconds  \
rows                                                        1788   
sum                                                    1376640.0   
mean                                                  769.932886   
median                                                     600.0   
mode           0    600.0
Name: trip_duration_seconds, dtype:...   
max                                                       5100.0   
min                                                        300.0   
std_dev                                               387.608563   
variance                                           150240.398403   
skewness                                                3.422645   
kurtosis                                               26.199345   
percentile_25                                              600.0   
percentile_75                                              900.0   
iqr                                                        300.0   
range                                                     4800.0   
cv                                                      0.503432   
qd                                                           0.2   
cs                                                       0.00883   
ck                                                      0.067592   
cvs                                                      0.00883   
cvk                                                     0.067592   
cvcs                                                     0.00883   
cvck                                                    0.067592   
cvcv                                                    0.503432   
cvqd                                                         0.2   
cvr                                                      6.23431   
cvm                                                          1.0   
cvmed                                                   0.779289   
cvmode         0    0.779289
Name: trip_duration_seconds, dty...   

column                                  trip_distance_kilometers  
rows                                                        1788  
sum                                                  2625.773526  
mean                                                    1.468553  
median                                                  1.248171  
mode           0    0.834842
Name: trip_distance_kilometers, ...  
max                                                     7.323831  
min                                                     0.100317  
std_dev                                                 1.023259  
variance                                                1.047059  
skewness                                                1.571946  
kurtosis                                                  3.4555  
percentile_25                                           0.770483  
percentile_75                                           1.928603  
iqr                                                      1.15812  
range                                                   7.223514  
cv                                                       0.69678  
qd                                                      0.429078  
cs                                                      1.536215  
ck                                                      3.376955  
cvs                                                     1.536215  
cvk                                                     3.376955  
cvcs                                                    1.536215  
cvck                                                    3.376955  
cvcv                                                     0.69678  
cvqd                                                    0.429078  
cvr                                                     4.918796  
cvm                                                          1.0  
cvmed                                                   0.849932  
cvmode         0

In [43]:
morning_rush_no_delay = no_delay[(no_delay['scheduled_arrival_time'].dt.hour >= 6) & (no_delay['scheduled_arrival_time'].dt.hour <= 9)]
morning_rush_no_delay

route_id  agency_id route_short_name  route_type route_type_name  \
2657          608          6              608           3             Bus   
2659          605          6              605           3             Bus   
2672          611          6              611           3             Bus   
2673          612          6              612           3             Bus   
2675          606          6              606           3             Bus   
...           ...        ...              ...         ...             ...   
2494920       609          6              609           3             Bus   
2494922       600          6              600           3             Bus   
2494924       601          6              601           3             Bus   
2494926       800         12              800           3             Bus   
2494927        65          6               65           0            Tram   

                                         agency_name  service_id  \
2657               SWB Stadtwerke Bonn Verkehrs GmbH         130   
2659               SWB Stadtwerke Bonn Verkehrs GmbH         130   
2672               SWB Stadtwerke Bonn Verkehrs GmbH          43   
2673               SWB Stadtwerke Bonn Verkehrs GmbH          43   
2675               SWB Stadtwerke Bonn Verkehrs GmbH          43   
...                                              ...         ...   
2494920            SWB Stadtwerke Bonn Verkehrs GmbH          64   
2494922            SWB Stadtwerke Bonn Verkehrs GmbH          64   
2494924            SWB Stadtwerke Bonn Verkehrs GmbH          64   
2494926  RVK Regionalverkehr Köln GmbH NL Meckenheim          64   
2494927            SWB Stadtwerke Bonn Verkehrs GmbH       26825   

                                                   trip_id  \
2657     6080121-608-006-687.2.26:053300-25-1_FAFFF268-...   
2659     6050124-605-006-687.2.34:054200-19-1_BDBC7386-...   
2672     6110003-611-006-1723.2.21:052000-60-1_65AA540D...   
2673     6120004-612-006-1280.2.22:055800-36-1_7F6838D0...   
2675     6060004-606-006-1584.2.22:054000-44-1_9B6D17A0...   
...                                                    ...   
2494920  6090048-609-006-1574.2.24:091900-45-1_963E3448...   
2494922  6000028-600-006-8813.2.22:095900-32-1_53EFFD6B...   
2494924  6010061-601-006-1293.2.21:095900-46-1_44BE0AA0...   
2494926  14-800-012-1690.2.22:092600-26-1_CD076C67-B58E...   
2494927  651030-65-006-1406.1.12:094400-24-179_3601D3CC...   

                       trip_headsign  direction_id  ...  delay_span  \
2657                         Gielgen             0  ...           0   
2659                     Duisdorf Bf             1  ...           0   
2672            Lessenich Sportplatz             0  ...           0   
2673                    Mehlem Fähre             1  ...           0   
2675              Hardtberg Klinikum             1  ...           0   
...                              ...           ...  ...         ...   
2494920           Hardthöhe/Südwache             1  ...           0   
2494922          Ippendorf Altenheim             1  ...           0   
2494924           Agnetendorfer Str.             0  ...           0   
2494926                     Bonn Hbf             1  ...           0   
2494927  Oberkassel Süd/Römlinghoven             1  ...           0   

         arrival_delay_span weather_int time_span_arrival  \
2657                      0           0     early morning   
2659                      0           0     early morning   
2672                      0           0     early morning   
2673                      0           0     early morning   
2675                      0           0     early morning   
...                     ...         ...               ...   
2494920                   0           1      morning rush   
2494922                   0           1                 0   
2494924                   0           1                 0   
2494926                   0           1                 0  

In [44]:
get_stats(morning_rush_no_delay, ['tier_trips_count', 'tier_trips_end_at_station_count', 'nextbike_trips_count', 'nextbike_trips_end_at_station_count', 'current_temp', 'current_precipitation_volume'])

/tmp/ipykernel_2575952/41814695.py:51: RuntimeWarning: invalid value encountered in scalar divide
  qd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:55: RuntimeWarning: invalid value encountered in scalar divide
  cvqd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:51: RuntimeWarning: invalid value encountered in scalar divide
  qd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:55: RuntimeWarning: invalid value encountered in scalar divide
  cvqd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:51: RuntimeWarning: invalid value encountered in scalar divide
  qd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:55: RuntimeWarning: invalid value encountered in scalar divide
  cvqd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:51: RuntimeWarning: invalid value encountered in scalar divide
  qd = iqr / (percentile_75 + percenti

column                                        tier_trips_count  \
rows                                                    122186   
sum                                                       2188   
mean                                                  0.017907   
median                                                     0.0   
mode               0    0
Name: tier_trips_count, dtype: int64   
max                                                          6   
min                                                          0   
std_dev                                               0.141048   
variance                                              0.019895   
skewness                                              9.008747   
kurtosis                                            108.917264   
percentile_25                                              0.0   
percentile_75                                              0.0   
iqr                                                        0.0   
range                                                        6   
cv                                                    7.876649   
qd                                                         NaN   
cs                                                   63.870015   
ck                                                  772.199184   
cvs                                                  63.870015   
cvk                                                 772.199184   
cvcs                                                 63.870015   
cvck                                                772.199184   
cvcv                                                  7.876649   
cvqd                                                       NaN   
cvr                                                 335.062157   
cvm                                                        1.0   
cvmed                                                      0.0   
cvmode         0    0.0
Name: tier_trips_count, dtype: float64   

column                           tier_trips_end_at_station_count  \
rows                                                      122186   
sum                                                         1784   
mean                                                    0.014601   
median                                                       0.0   
mode           0    0
Name: tier_trips_end_at_station_count, ...   
max                                                            6   
min                                                            0   
std_dev                                                 0.126134   
variance                                                 0.01591   
skewness                                                 9.86344   
kurtosis                                              135.206654   
percentile_25                                                0.0   
percentile_75                                                0.0   
iqr                                                          0.0   
range                                                          6   
cv                                                       8.63894   
qd                                                           NaN   
cs                                                     78.197806   
ck                                                   1071.924509   
cvs                                                    78.197806   
cvk                                                  1071.924509   
cvcs                                                   78.197806   
cvck                                                 1071.924509   
cvcv                                                     8.63894   
cvqd                                                         NaN   
cvr                                                   410.939462   
cvm                                                          1.0   
cvmed                                                        0.0   
cvmode         0    0.0
Name: tier_trips_end_at

In [45]:
morning_rush_no_delay_tier = check_micromobility_datasets('tier', morning_rush_no_delay)

In [46]:
morning_rush_no_delay_tier.describe()

tier_trips_id          tier_trips_start_time  \
count   8.960000e+02                            896   
mean    7.962484e+08  2023-07-14 19:02:33.013393152   
min     7.822651e+08            2023-07-01 06:35:00   
25%     7.823735e+08            2023-07-07 09:18:45   
50%     7.824554e+08            2023-07-13 08:30:00   
75%     8.087154e+08            2023-07-21 08:41:15   
max     8.323097e+08            2023-07-31 09:50:00   
std     1.565802e+07                            NaN   

                 tier_trips_end_time              trip_duration  \
count                            896                        896   
mean   2023-07-14 19:15:43.191964416  0 days 00:13:10.178571428   
min              2023-07-01 06:40:00            0 days 00:05:00   
25%              2023-07-07 09:33:45            0 days 00:10:00   
50%              2023-07-13 08:40:00            0 days 00:10:00   
75%              2023-07-21 08:50:00            0 days 00:15:00   
max              2023-07-31 10:05:00            0 days 01:40:00   
std                              NaN  0 days 00:08:53.831487889   

       trip_distance_kilometers  trip_distance_meters  start_stop_id  \
count                896.000000            896.000000     685.000000   
mean                   1.628683           1628.682599    1253.456934   
min                    0.100712            100.712421     161.000000   
25%                    0.684428            684.427915     687.000000   
50%                    1.259686           1259.686419    1115.000000   
75%                    2.194210           2194.210482    1411.000000   
max                    8.725601           8725.600930    9703.000000   
std                    1.332542           1332.542318    1243.497372   

       end_stop_id  trip_duration_seconds  
count   466.000000             896.000000  
mean   1296.156652             790.178571  
min      43.000000             300.000000  
25%     697.000000             600.000000  
50%    1135.000000             600.000000  
75%    1234.000000             900.000000  
max    9780.000000            6000.000000  
std    1291.741916             533.831488

In [47]:
get_stats(morning_rush_no_delay_tier, ['trip_duration_seconds', 'trip_distance_kilometers'])

column                                     trip_duration_seconds  \
rows                                                         896   
sum                                                     708000.0   
mean                                                  790.178571   
median                                                     600.0   
mode           0    600.0
Name: trip_duration_seconds, dtype:...   
max                                                       6000.0   
min                                                        300.0   
std_dev                                               533.831488   
variance                                           284976.057462   
skewness                                                4.079903   
kurtosis                                               27.703959   
percentile_25                                              600.0   
percentile_75                                              900.0   
iqr                                                        300.0   
range                                                     5700.0   
cv                                                      0.675583   
qd                                                           0.2   
cs                                                      0.007643   
ck                                                      0.051896   
cvs                                                     0.007643   
cvk                                                     0.051896   
cvcs                                                    0.007643   
cvck                                                    0.051896   
cvcv                                                    0.675583   
cvqd                                                         0.2   
cvr                                                     7.213559   
cvm                                                          1.0   
cvmed                                                   0.759322   
cvmode         0    0.759322
Name: trip_duration_seconds, dty...   

column                                  trip_distance_kilometers  
rows                                                         896  
sum                                                  1459.299609  
mean                                                    1.628683  
median                                                  1.259686  
mode           0      0.100712
1      0.105761
2      0.10668...  
max                                                     8.725601  
min                                                     0.100712  
std_dev                                                 1.332542  
variance                                                1.775669  
skewness                                                1.766377  
kurtosis                                                4.018807  
percentile_25                                           0.684428  
percentile_75                                            2.19421  
iqr                                                     1.509783  
range                                                   8.624889  
cv                                                      0.818172  
qd                                                      0.524478  
cs                                                      1.325569  
ck                                                      3.015894  
cvs                                                     1.325569  
cvk                                                     3.015894  
cvcs                                                    1.325569  
cvck                                                    3.015894  
cvcv                                                    0.818172  
cvqd                                                    0.524478  
cvr                                                     5.295623  
cvm                                                          1.0  
cvmed                                                   0.773439  
cvmode         0

In [48]:
# get entries where trips start and end at station
morning_rush_no_delay_tier_station_station = morning_rush_no_delay_tier[morning_rush_no_delay_tier['end_stop_id'].notna() & morning_rush_no_delay_tier['start_stop_id'].notna()]
morning_rush_no_delay_tier_station_station

tier_trips_id tier_trips_start_time tier_trips_end_time vehicle type  \
3030326      782303335   2023-07-01 07:15:00 2023-07-01 07:25:00    e-scooter   
3173737      782357914   2023-07-01 07:50:00 2023-07-01 07:55:00    e-scooter   
3030331      782303340   2023-07-01 08:05:00 2023-07-01 08:20:00    e-scooter   
3181011      782364568   2023-07-01 08:10:00 2023-07-01 08:20:00    e-scooter   
2965749      782283914   2023-07-01 08:15:00 2023-07-01 08:25:00    e-scooter   
...                ...                   ...                 ...          ...   
3325477      832124843   2023-07-31 09:20:00 2023-07-31 09:30:00    e-scooter   
3416876      832199842   2023-07-31 09:40:00 2023-07-31 09:50:00    e-scooter   
3330682      832128386   2023-07-31 09:40:00 2023-07-31 09:55:00    e-scooter   
3402428      832186021   2023-07-31 09:45:00 2023-07-31 09:50:00    e-scooter   
3453395      832234899   2023-07-31 09:50:00 2023-07-31 10:05:00    e-scooter   

          trip_duration  trip_distance_kilometers  trip_distance_meters  \
3030326 0 days 00:10:00                  1.594246           1594.246052   
3173737 0 days 00:05:00                  1.121445           1121.445299   
3030331 0 days 00:15:00                  1.614868           1614.867979   
3181011 0 days 00:10:00                  0.463702            463.702206   
2965749 0 days 00:10:00                  0.860218            860.218080   
...                 ...                       ...                   ...   
3325477 0 days 00:10:00                  0.920274            920.273564   
3416876 0 days 00:10:00                  3.058432           3058.432358   
3330682 0 days 00:15:00                  1.125842           1125.841563   
3402428 0 days 00:05:00                  0.406598            406.597728   
3453395 0 days 00:15:00                  2.005188           2005.187551   

         start_stop_id                            start_stop_name  \
3030326          688.0                                  Bonn West   
3173737         1181.0                           Bonn Am Nordpark   
3030331         1175.0                            Bonn Lvr-Klinik   
3181011         1102.0                         Bonn Friedensplatz   
2965749         1110.0                         Bonn Wilhelmsplatz   
...                ...                                        ...   
3325477         1525.0                         Bonn Geislar Mitte   
3416876         1115.0  Bonn Bertha-Von-Suttner-Pl./Beethovenhaus   
3330682         1102.0                         Bonn Friedensplatz   
3402428         1500.0                 Bonn Konrad-Adenauer-Platz   
3453395         1115.0  Bonn Bertha-Von-Suttner-Pl./Beethovenhaus   

                                         start_buffer_zone  end_stop_id  \
3030326  801621     POLYGON ((7.157885983913106 50.7227...       1175.0   
3173737  801621     POLYGON ((7.157885983913106 50.7227...       2738.0   
3030331  801621     POLYGON ((7.157885983913106 50.7227...        688.0   
3181011  801621     POLYGON ((7.157885983913106 50.7227...       1115.0   
2965749  801621     POLYGON ((7.157885983913106 50.7227...        687.0   
...                                                    ...          ...   
3325477  801621     POLYGON ((7.157885983913106 50.7227...       1523.0   
3416876  801621     POLYGON ((7.157885983913106 50.7227...       1540.0   
3330682  801621     POLYGON ((7.157885983913106 50.7227...       1175.0   
3402428  801621     POLYGON ((7.157885983913106 50.7227...       8635.0   
3453395  801621     POLYGON ((7.157885983913106 50.7227...       1500.0   

                                     end_stop_name  \
3030326                            Bonn Lvr-Klinik   
3173737                          Bonn Hedwigschule   
3030331                                  Bonn West   
3181011  Bonn Bertha-Von-Suttner-Pl./Beethovenhaus   
2965749                                   Bonn Hbf   
...                                            ...   
3325477                    

In [49]:
morning_rush_no_delay_tier_station_station.describe()

tier_trips_id          tier_trips_start_time  \
count   4.090000e+02                            409   
mean    7.947326e+08  2023-07-13 22:28:24.645476608   
min     7.822651e+08            2023-07-01 07:15:00   
25%     7.823624e+08            2023-07-07 07:30:00   
50%     7.824452e+08            2023-07-12 06:40:00   
75%     8.087028e+08            2023-07-20 10:00:00   
max     8.323097e+08            2023-07-31 09:50:00   
std     1.509510e+07                            NaN   

                 tier_trips_end_time              trip_duration  \
count                            409                        409   
mean   2023-07-13 22:40:29.339853056  0 days 00:12:04.694376528   
min              2023-07-01 07:25:00            0 days 00:05:00   
25%              2023-07-07 07:40:00            0 days 00:10:00   
50%              2023-07-12 06:50:00            0 days 00:10:00   
75%              2023-07-20 10:30:00            0 days 00:15:00   
max              2023-07-31 10:05:00            0 days 01:40:00   
std                              NaN  0 days 00:07:45.739415267   

       trip_distance_kilometers  trip_distance_meters  start_stop_id  \
count                409.000000            409.000000     409.000000   
mean                   1.327826           1327.825980    1268.936430   
min                    0.105761            105.761295     161.000000   
25%                    0.617976            617.975863     694.000000   
50%                    1.101235           1101.234729    1115.000000   
75%                    1.810488           1810.487531    1255.000000   
max                    6.209313           6209.312760    9703.000000   
std                    0.974341            974.341179    1161.925667   

       end_stop_id  trip_duration_seconds  
count   409.000000             409.000000  
mean   1314.496333             724.694377  
min      43.000000             300.000000  
25%    1102.000000             600.000000  
50%    1140.000000             600.000000  
75%    1240.000000             900.000000  
max    9780.000000            6000.000000  
std    1262.660982             465.739415

In [50]:
# get statistics for the tier trips that start and end at a station
get_stats(morning_rush_no_delay_tier_station_station, ['trip_duration_seconds', 'trip_distance_kilometers'])

column                                     trip_duration_seconds  \
rows                                                         409   
sum                                                     296400.0   
mean                                                  724.694377   
median                                                     600.0   
mode           0    600.0
Name: trip_duration_seconds, dtype:...   
max                                                       6000.0   
min                                                        300.0   
std_dev                                               465.739415   
variance                                           216913.202934   
skewness                                                  5.1664   
kurtosis                                               45.861059   
percentile_25                                              600.0   
percentile_75                                              900.0   
iqr                                                        300.0   
range                                                     5700.0   
cv                                                       0.64267   
qd                                                           0.2   
cs                                                      0.011093   
ck                                                      0.098469   
cvs                                                     0.011093   
cvk                                                     0.098469   
cvcs                                                    0.011093   
cvck                                                    0.098469   
cvcv                                                     0.64267   
cvqd                                                         0.2   
cvr                                                     7.865385   
cvm                                                          1.0   
cvmed                                                   0.827935   
cvmode         0    0.827935
Name: trip_duration_seconds, dty...   

column                                  trip_distance_kilometers  
rows                                                         409  
sum                                                   543.080826  
mean                                                    1.327826  
median                                                  1.101235  
mode           0      0.105761
1      0.106681
2      0.11022...  
max                                                     6.209313  
min                                                     0.105761  
std_dev                                                 0.974341  
variance                                                0.949341  
skewness                                                1.314879  
kurtosis                                                2.371615  
percentile_25                                           0.617976  
percentile_75                                           1.810488  
iqr                                                     1.192512  
range                                                   6.103551  
cv                                                      0.733787  
qd                                                      0.491056  
cs                                                      1.349506  
ck                                                       2.43407  
cvs                                                     1.349506  
cvk                                                      2.43407  
cvcs                                                    1.349506  
cvck                                                     2.43407  
cvcv                                                    0.733787  
cvqd                                                    0.491056  
cvr                                                      4.59665  
cvm                                                          1.0  
cvmed                                                   0.829352  
cvmode         0

In [51]:
morning_rush_no_delay_next = check_micromobility_datasets('next', morning_rush_no_delay)

In [52]:
morning_rush_no_delay_next.describe()

nextbike_trips_id      nextbike_trips_start_time  \
count       3.189000e+03                           3189   
mean        3.793740e+07  2023-07-15 04:13:29.802445824   
min         3.771654e+07            2023-07-01 06:11:00   
25%         3.782630e+07            2023-07-08 06:11:00   
50%         3.794002e+07            2023-07-14 06:26:00   
75%         3.804579e+07            2023-07-21 08:01:00   
max         3.817174e+07            2023-07-31 10:01:00   
std         1.279608e+05                            NaN   

             nextbike_trips_end_time              trip_duration  \
count                           3189                       3189   
mean   2023-07-15 04:27:25.531514624  0 days 00:13:55.729068673   
min              2023-07-01 06:36:00            0 days 00:05:00   
25%              2023-07-08 06:26:00            0 days 00:10:00   
50%              2023-07-14 06:36:00            0 days 00:10:00   
75%              2023-07-21 08:16:00            0 days 00:15:00   
max              2023-07-31 11:56:00            0 days 02:00:00   
std                              NaN  0 days 00:08:59.954872270   

       trip_distance_kilometers  trip_distance_meters  start_stop_id  \
count               3189.000000           3189.000000    2653.000000   
mean                   1.649911           1649.911080    1069.671692   
min                    0.100004            100.003661      43.000000   
25%                    0.804092            804.092268     687.000000   
50%                    1.316158           1316.157638    1115.000000   
75%                    2.121177           2121.176840    1221.000000   
max                   10.228192          10228.191572    9780.000000   
std                    1.282954           1282.954346     765.345298   

       end_stop_id  trip_duration_seconds  
count  1888.000000            3189.000000  
mean   1125.825742             835.729069  
min      43.000000             300.000000  
25%     687.000000             600.000000  
50%    1140.000000             600.000000  
75%    1221.000000             900.000000  
max    9702.000000            7200.000000  
std     852.770909             539.954872

In [53]:
get_stats(morning_rush_no_delay_next, ['trip_duration_seconds', 'trip_distance_kilometers'])

column                                     trip_duration_seconds  \
rows                                                        3189   
sum                                                    2665140.0   
mean                                                  835.729069   
median                                                     600.0   
mode           0    600.0
Name: trip_duration_seconds, dtype:...   
max                                                       7200.0   
min                                                        300.0   
std_dev                                               539.954872   
variance                                           291551.264089   
skewness                                                 4.84564   
kurtosis                                               40.791871   
percentile_25                                              600.0   
percentile_75                                              900.0   
iqr                                                        300.0   
range                                                     6900.0   
cv                                                      0.646088   
qd                                                           0.2   
cs                                                      0.008974   
ck                                                      0.075547   
cvs                                                     0.008974   
cvk                                                     0.075547   
cvcs                                                    0.008974   
cvck                                                    0.075547   
cvcv                                                    0.646088   
cvqd                                                         0.2   
cvr                                                     8.256264   
cvm                                                          1.0   
cvmed                                                   0.717936   
cvmode         0    0.717936
Name: trip_duration_seconds, dty...   

column                                  trip_distance_kilometers  
rows                                                        3189  
sum                                                  5261.566433  
mean                                                    1.649911  
median                                                  1.316158  
mode           0    1.482255
Name: trip_distance_kilometers, ...  
max                                                    10.228192  
min                                                     0.100004  
std_dev                                                 1.282954  
variance                                                1.645972  
skewness                                                1.902839  
kurtosis                                                5.232149  
percentile_25                                           0.804092  
percentile_75                                           2.121177  
iqr                                                     1.317085  
range                                                  10.128188  
cv                                                       0.77759  
qd                                                      0.450244  
cs                                                       1.48317  
ck                                                      4.078203  
cvs                                                      1.48317  
cvk                                                     4.078203  
cvcs                                                     1.48317  
cvck                                                    4.078203  
cvcv                                                     0.77759  
cvqd                                                    0.450244  
cvr                                                     6.138627  
cvm                                                          1.0  
cvmed                                                   0.797714  
cvmode         0

In [54]:
# get entries where trips start and end at station
morning_rush_no_delay_next_station_station = morning_rush_no_delay_next[morning_rush_no_delay_next['end_stop_id'].notna() & morning_rush_no_delay_next['start_stop_id'].notna()]
morning_rush_no_delay_next_station_station

nextbike_trips_id nextbike_trips_start_time nextbike_trips_end_time  \
1433891           38006735       2023-07-01 06:21:00     2023-07-01 06:36:00   
1471081           38035639       2023-07-01 06:26:00     2023-07-01 06:41:00   
1269781           37830049       2023-07-01 06:31:00     2023-07-01 06:46:00   
1488023           38048406       2023-07-01 06:31:00     2023-07-01 06:41:00   
1488024           38048407       2023-07-01 06:41:00     2023-07-01 06:51:00   
...                    ...                       ...                     ...   
1259040           37739036       2023-07-31 09:36:00     2023-07-31 09:46:00   
1463109           37974425       2023-07-31 09:46:00     2023-07-31 10:01:00   
1372188           37915372       2023-07-31 09:51:00     2023-07-31 10:01:00   
1380556           37942216       2023-07-31 09:51:00     2023-07-31 10:01:00   
1563208           38167336       2023-07-31 09:56:00     2023-07-31 11:56:00   

         nextbike_trips_start_at_station  nextbike_trips_end_at_station  \
1433891                            False                          False   
1471081                            False                          False   
1269781                            False                          False   
1488023                            False                           True   
1488024                             True                          False   
...                                  ...                            ...   
1259040                            False                          False   
1463109                            False                          False   
1372188                            False                          False   
1380556                            False                          False   
1563208                             True                           True   

        vehicle type   trip_duration  trip_distance_kilometers  \
1433891         bike 0 days 00:15:00                  1.550245   
1471081         bike 0 days 00:15:00                  1.898569   
1269781         bike 0 days 00:15:00                  1.402119   
1488023         bike 0 days 00:10:00                  0.313697   
1488024         bike 0 days 00:10:00                  1.163671   
...              ...             ...                       ...   
1259040         bike 0 days 00:10:00                  1.720626   
1463109         bike 0 days 00:15:00                  2.142474   
1372188         bike 0 days 00:10:00                  0.861798   
1380556         bike 0 days 00:10:00                  1.469940   
1563208         bike 0 days 02:00:00                  3.481091   

         trip_distance_meters  \
1433891           1550.245342   
1471081           1898.568609   
1269781           1402.119138   
1488023            313.697078   
1488024           1163.670584   
...                       ...   
1259040           1720.625521   
1463109           2142.474179   
1372188            861.797638   
1380556           1469.940334   
1563208           3481.090632   

                                            start_location  \
1433891  b'\x01\x01\x00\x00\x00\xa9lXSYT\x1c@\xb0\xe6\x...   
1471081  b'\x01\x01\x00\x00\x00\xbb\x99\xd1\x8f\x86c\x1...   
1269781  b'\x01\x01\x00\x00\x00N\xd1\x91\\\xfec\x1c@\xf...   
1488023  b'\x01\x01\x00\x00\x00\xd2\xc2e\x156c\x1c@\x8b...   
1488024  b'\x01\x01\x00\x00\x00\x06.\x8f5#c\x1c@\x9dJ\x...   
...                                                    ...   
1259040  b'\x01\x01\x00\x00\x00C:<\x84\xf1c\x1c@\xda \x...   
1463109  b'\x01\x01\x00\x00\x00\x97\x1a\xa1\x9f\xa9W\x1...   
1372188  b'\x01\x01\x00\x00\x00\xd9\xb1\x11\x88\xd7U\x1...   
1380556   b'\x01\x01\x00\x00\x00t(CULU\x1c@"\x8euq\x1b]I@'   
1563208  b'\x01\x01\x00\x00\x00&\x199\x0b{Z\x1c@\xb4\xe...   

                                              end_location  start_stop_id  \
1433891  b'\x01\x01\x00\x00\x00\xdapX\x1a\xf8a\x1c@(\x0...         1221.0   
1471081  b'\x01\x01\x00\x00\x00#.\x00\x8d\xd2e\x1c@\xd5...

In [55]:
morning_rush_no_delay_next_station_station.describe()

nextbike_trips_id      nextbike_trips_start_time  \
count       1.644000e+03                           1644   
mean        3.793725e+07  2023-07-14 19:28:46.897810176   
min         3.771654e+07            2023-07-01 06:21:00   
25%         3.782829e+07            2023-07-07 08:44:45   
50%         3.793795e+07            2023-07-13 09:11:00   
75%         3.804516e+07            2023-07-21 06:46:00   
max         3.817163e+07            2023-07-31 09:56:00   
std         1.273162e+05                            NaN   

             nextbike_trips_end_time              trip_duration  \
count                           1644                       1644   
mean   2023-07-14 19:41:54.379561984  0 days 00:13:07.481751824   
min              2023-07-01 06:36:00            0 days 00:05:00   
25%              2023-07-07 08:59:45            0 days 00:10:00   
50%              2023-07-13 09:26:00            0 days 00:10:00   
75%              2023-07-21 06:56:00            0 days 00:15:00   
max              2023-07-31 11:56:00            0 days 02:00:00   
std                              NaN  0 days 00:09:17.517525197   

       trip_distance_kilometers  trip_distance_meters  start_stop_id  \
count               1644.000000           1644.000000    1644.000000   
mean                   1.388695           1388.694696    1097.515207   
min                    0.100004            100.003661     161.000000   
25%                    0.735497            735.497294     687.000000   
50%                    1.201109           1201.109404    1115.000000   
75%                    1.783995           1783.995404    1221.000000   
max                    7.767933           7767.932546    9780.000000   
std                    0.998580            998.579600     729.099100   

       end_stop_id  trip_duration_seconds  
count  1644.000000            1644.000000  
mean   1155.956813             787.481752  
min      43.000000             300.000000  
25%     688.000000             600.000000  
50%    1141.000000             600.000000  
75%    1221.000000             900.000000  
max    9702.000000            7200.000000  
std     897.838988             557.517525

In [56]:
# get statistics for the tier trips that start and end at a station
get_stats(morning_rush_no_delay_next_station_station, ['trip_duration_seconds', 'trip_distance_kilometers'])

column                                     trip_duration_seconds  \
rows                                                        1644   
sum                                                    1294620.0   
mean                                                  787.481752   
median                                                     600.0   
mode           0    600.0
Name: trip_duration_seconds, dtype:...   
max                                                       7200.0   
min                                                        300.0   
std_dev                                               557.517525   
variance                                           310825.790902   
skewness                                                6.161867   
kurtosis                                               57.934879   
percentile_25                                              600.0   
percentile_75                                              900.0   
iqr                                                        300.0   
range                                                     6900.0   
cv                                                      0.707975   
qd                                                           0.2   
cs                                                      0.011052   
ck                                                      0.103916   
cvs                                                     0.011052   
cvk                                                     0.103916   
cvcs                                                    0.011052   
cvck                                                    0.103916   
cvcv                                                    0.707975   
cvqd                                                         0.2   
cvr                                                     8.762108   
cvm                                                          1.0   
cvmed                                                   0.761922   
cvmode         0    0.761922
Name: trip_duration_seconds, dty...   

column                                  trip_distance_kilometers  
rows                                                        1644  
sum                                                   2283.01408  
mean                                                    1.388695  
median                                                  1.201109  
mode           0    1.482255
Name: trip_distance_kilometers, ...  
max                                                     7.767933  
min                                                     0.100004  
std_dev                                                  0.99858  
variance                                                0.997161  
skewness                                                1.796315  
kurtosis                                                4.866705  
percentile_25                                           0.735497  
percentile_75                                           1.783995  
iqr                                                     1.048498  
range                                                   7.667929  
cv                                                      0.719078  
qd                                                      0.416154  
cs                                                       1.79887  
ck                                                      4.873628  
cvs                                                      1.79887  
cvk                                                     4.873628  
cvcs                                                     1.79887  
cvck                                                    4.873628  
cvcv                                                    0.719078  
cvqd                                                    0.416154  
cvr                                                     5.521681  
cvm                                                          1.0  
cvmed                                                    0.86492  
cvmode         0

In [57]:
morning_rush_nan_delay = nan_delay[(nan_delay['scheduled_arrival_time'].dt.hour >= 6) & (nan_delay['scheduled_arrival_time'].dt.hour <= 9)]
morning_rush_nan_delay

route_id  agency_id route_short_name  route_type route_type_name  \
2653          610          6              610           3             Bus   
2656          610          6              610           3             Bus   
2658          612          6              612           3             Bus   
2660          600          6              600           3             Bus   
2662          604          6              604           3             Bus   
...           ...        ...              ...         ...             ...   
2494906       603          6              603           3             Bus   
2494913       609          6              609           3             Bus   
2494921       605          6              605           3             Bus   
2494923       540          6              540           3             Bus   
2494928       608          6              608           3             Bus   

                               agency_name  service_id  \
2653     SWB Stadtwerke Bonn Verkehrs GmbH          43   
2656     SWB Stadtwerke Bonn Verkehrs GmbH          43   
2658     SWB Stadtwerke Bonn Verkehrs GmbH         130   
2660     SWB Stadtwerke Bonn Verkehrs GmbH         130   
2662     SWB Stadtwerke Bonn Verkehrs GmbH          43   
...                                    ...         ...   
2494906  SWB Stadtwerke Bonn Verkehrs GmbH          64   
2494913  SWB Stadtwerke Bonn Verkehrs GmbH          64   
2494921  SWB Stadtwerke Bonn Verkehrs GmbH          64   
2494923  SWB Stadtwerke Bonn Verkehrs GmbH          64   
2494928  SWB Stadtwerke Bonn Verkehrs GmbH          64   

                                                   trip_id  \
2653     6100003-610-006-1756.2.21:051000-54-1_22331419...   
2656     6100005-610-006-1756.2.21:054000-54-1_942CB978...   
2658     6120109-612-006-1763.2.21:053900-39-1_198A032D...   
2660     6000218-600-006-8813.2.22:054000-38-1_76B49E18...   
2662     6040003-604-006-1382.2.21:055600-49-1_37DB308A...   
...                                                    ...   
2494906  6030023-603-006-1386.2.21:091000-37-1_E15D6262...   
2494913  6090060-609-006-1574.2.24:085900-45-1_EF291F3C...   
2494921  6050025-605-006-1341.2.24:092600-40-1_BD980DE1...   
2494923  5400021-540-006-687.2.23:094400-32-1_9099DD74-...   
2494928  6080053-608-006-1374.2.21:092100-46-1_72BA3349...   

                  trip_headsign  direction_id  ...  delay_span  \
2653                Duisdorf Bf             0  ...           0   
2656                Duisdorf Bf             0  ...           0   
2658         Loki-Schmidt-Platz             0  ...           0   
2660        Ippendorf Altenheim             1  ...           0   
2662                     Hersel             0  ...           0   
...                         ...           ...  ...         ...   
2494906          Alte Schulstr.             0  ...           0   
2494913      Hardthöhe/Südwache             1  ...           0   
2494921         Mondorfer Fähre             0  ...           0   
2494923  Sankt Augustin Zentrum             1  ...           0   
2494928                 Gielgen             0  ...           0   

         arrival_delay_span weather_int time_span_arrival  \
2653                      0           0                 0   
2656                      0           0                 0   
2658                      0           0                 0   
2660                      0           0                 0   
2662                      0           0                 0   
...                     ...         ...               ...   
2494906                   0           1                 0   
2494913                   0           1                 0   
2494921                   0           1                 0   
2494923                   0           1                 0   
2494928                   0           1                 0   

         time_span_int_arrival  weekend time_span time_span_int  \
2653                         0        2         0

In [58]:
get_stats(morning_rush_nan_delay, ['tier_trips_count', 'tier_trips_end_at_station_count', 'nextbike_trips_count', 'nextbike_trips_end_at_station_count', 'current_temp', 'current_precipitation_volume'])

/tmp/ipykernel_2575952/41814695.py:51: RuntimeWarning: invalid value encountered in scalar divide
  qd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:55: RuntimeWarning: invalid value encountered in scalar divide
  cvqd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:51: RuntimeWarning: invalid value encountered in scalar divide
  qd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:55: RuntimeWarning: invalid value encountered in scalar divide
  cvqd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:51: RuntimeWarning: invalid value encountered in scalar divide
  qd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:55: RuntimeWarning: invalid value encountered in scalar divide
  cvqd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:51: RuntimeWarning: invalid value encountered in scalar divide
  qd = iqr / (percentile_75 + percenti

column                                        tier_trips_count  \
rows                                                    222593   
sum                                                       2621   
mean                                                  0.011775   
median                                                     0.0   
mode               0    0
Name: tier_trips_count, dtype: int64   
max                                                          5   
min                                                          0   
std_dev                                               0.112559   
variance                                               0.01267   
skewness                                             10.474828   
kurtosis                                            134.145101   
percentile_25                                              0.0   
percentile_75                                              0.0   
iqr                                                        0.0   
range                                                        5   
cv                                                    9.559274   
qd                                                         NaN   
cs                                                    93.06074   
ck                                                 1191.775367   
cvs                                                   93.06074   
cvk                                                1191.775367   
cvcs                                                  93.06074   
cvck                                               1191.775367   
cvcv                                                  9.559274   
cvqd                                                       NaN   
cvr                                                 424.633728   
cvm                                                        1.0   
cvmed                                                      0.0   
cvmode         0    0.0
Name: tier_trips_count, dtype: float64   

column                           tier_trips_end_at_station_count  \
rows                                                      222593   
sum                                                         2149   
mean                                                    0.009654   
median                                                       0.0   
mode           0    0
Name: tier_trips_end_at_station_count, ...   
max                                                            4   
min                                                            0   
std_dev                                                 0.100902   
variance                                                0.010181   
skewness                                               11.077943   
kurtosis                                              138.116025   
percentile_25                                                0.0   
percentile_75                                                0.0   
iqr                                                          0.0   
range                                                          4   
cv                                                       10.4514   
qd                                                           NaN   
cs                                                    109.789224   
ck                                                   1368.814759   
cvs                                                   109.789224   
cvk                                                  1368.814759   
cvcs                                                  109.789224   
cvck                                                 1368.814759   
cvcv                                                     10.4514   
cvqd                                                         NaN   
cvr                                                   414.319218   
cvm                                                          1.0   
cvmed                                                        0.0   
cvmode         0    0.0
Name: tier_trips_end_at

In [59]:
morning_rush_nan_delay_tier = check_micromobility_datasets('tier', morning_rush_nan_delay)

In [60]:
morning_rush_nan_delay_tier.describe()

tier_trips_id          tier_trips_start_time  \
count   1.299000e+03                           1299   
mean    7.961287e+08  2023-07-14 14:07:12.794457088   
min     7.822651e+08            2023-07-01 06:15:00   
25%     7.823674e+08            2023-07-07 09:02:30   
50%     7.824542e+08            2023-07-13 07:30:00   
75%     8.087177e+08            2023-07-21 07:52:30   
max     8.323071e+08            2023-07-31 09:45:00   
std     1.564114e+07                            NaN   

                 tier_trips_end_time              trip_duration  \
count                           1299                       1299   
mean   2023-07-14 14:20:11.085450496  0 days 00:12:58.290993071   
min              2023-07-01 06:25:00            0 days 00:05:00   
25%              2023-07-07 09:15:00            0 days 00:10:00   
50%              2023-07-13 07:35:00            0 days 00:10:00   
75%              2023-07-21 08:05:00            0 days 00:15:00   
max              2023-07-31 10:00:00            0 days 01:40:00   
std                              NaN  0 days 00:08:03.333798597   

       trip_distance_kilometers  trip_distance_meters  start_stop_id  \
count               1299.000000           1299.000000     952.000000   
mean                   1.645078           1645.077555    1440.821429   
min                    0.100042            100.042262      43.000000   
25%                    0.704948            704.948268    1102.000000   
50%                    1.295517           1295.516735    1135.500000   
75%                    2.154041           2154.041400    1311.000000   
max                   10.280889          10280.888852    9703.000000   
std                    1.359789           1359.788742    1534.401700   

       end_stop_id  trip_duration_seconds  
count   699.000000            1299.000000  
mean   1289.237482             778.290993  
min      43.000000             300.000000  
25%     698.000000             600.000000  
50%    1126.000000             600.000000  
75%    1223.000000             900.000000  
max    9780.000000            6000.000000  
std    1304.442085             483.333799

In [61]:
get_stats(morning_rush_nan_delay_tier, ['trip_duration_seconds', 'trip_distance_kilometers'])

column                                     trip_duration_seconds  \
rows                                                        1299   
sum                                                    1011000.0   
mean                                                  778.290993   
median                                                     600.0   
mode           0    600.0
Name: trip_duration_seconds, dtype:...   
max                                                       6000.0   
min                                                        300.0   
std_dev                                               483.333799   
variance                                           233611.560866   
skewness                                                3.645588   
kurtosis                                               23.873134   
percentile_25                                              600.0   
percentile_75                                              900.0   
iqr                                                        300.0   
range                                                     5700.0   
cv                                                      0.621019   
qd                                                           0.2   
cs                                                      0.007543   
ck                                                      0.049393   
cvs                                                     0.007543   
cvk                                                     0.049393   
cvcs                                                    0.007543   
cvck                                                    0.049393   
cvcv                                                    0.621019   
cvqd                                                         0.2   
cvr                                                     7.323739   
cvm                                                          1.0   
cvmed                                                    0.77092   
cvmode         0    0.77092
Name: trip_duration_seconds, dtyp...   

column                                  trip_distance_kilometers  
rows                                                        1299  
sum                                                  2136.955744  
mean                                                    1.645078  
median                                                  1.295517  
mode           0        0.100042
1        0.105761
2        0...  
max                                                    10.280889  
min                                                     0.100042  
std_dev                                                 1.359789  
variance                                                1.849025  
skewness                                                1.921454  
kurtosis                                                5.238876  
percentile_25                                           0.704948  
percentile_75                                           2.154041  
iqr                                                     1.449093  
range                                                  10.180847  
cv                                                       0.82658  
qd                                                      0.506855  
cs                                                      1.413053  
ck                                                      3.852713  
cvs                                                     1.413053  
cvk                                                     3.852713  
cvcs                                                    1.413053  
cvck                                                    3.852713  
cvcv                                                     0.82658  
cvqd                                                    0.506855  
cvr                                                     6.188673  
cvm                                                          1.0  
cvmed                                                   0.787511  
cvmode         0

In [62]:
# get entries where trips start and end at station
morning_rush_nan_delay_tier_station_station = morning_rush_nan_delay_tier[morning_rush_nan_delay_tier['end_stop_id'].notna() & morning_rush_nan_delay_tier['start_stop_id'].notna()]
morning_rush_nan_delay_tier_station_station

tier_trips_id tier_trips_start_time tier_trips_end_time vehicle type  \
3284125      782459285   2023-07-01 06:25:00 2023-07-01 06:35:00    e-scooter   
2960244      782282011   2023-07-01 07:20:00 2023-07-01 07:35:00    e-scooter   
3109531      782329093   2023-07-01 07:25:00 2023-07-01 07:45:00    e-scooter   
2999342      782294477   2023-07-01 07:30:00 2023-07-01 07:35:00    e-scooter   
3181011      782364568   2023-07-01 08:10:00 2023-07-01 08:20:00    e-scooter   
...                ...                   ...                 ...          ...   
3473714      832254380   2023-07-31 08:45:00 2023-07-31 08:55:00    e-scooter   
3418794      832201669   2023-07-31 09:30:00 2023-07-31 09:35:00    e-scooter   
3416876      832199842   2023-07-31 09:40:00 2023-07-31 09:50:00    e-scooter   
3330682      832128386   2023-07-31 09:40:00 2023-07-31 09:55:00    e-scooter   
3402428      832186021   2023-07-31 09:45:00 2023-07-31 09:50:00    e-scooter   

          trip_duration  trip_distance_kilometers  trip_distance_meters  \
3284125 0 days 00:10:00                  1.058008           1058.008151   
2960244 0 days 00:15:00                  0.978814            978.814372   
3109531 0 days 00:20:00                  1.863754           1863.753840   
2999342 0 days 00:05:00                  0.458642            458.641594   
3181011 0 days 00:10:00                  0.463702            463.702206   
...                 ...                       ...                   ...   
3473714 0 days 00:10:00                  0.211118            211.118491   
3418794 0 days 00:05:00                  0.179043            179.042874   
3416876 0 days 00:10:00                  3.058432           3058.432358   
3330682 0 days 00:15:00                  1.125842           1125.841563   
3402428 0 days 00:05:00                  0.406598            406.597728   

         start_stop_id                            start_stop_name  \
3284125         1128.0                            Bonn Gartenstr.   
2960244         1513.0                      Bonn Rheindorfer Str.   
3109531         1102.0                         Bonn Friedensplatz   
2999342         2667.0  Bonn Brüdergasse/Bertha-Von-Suttner-Platz   
3181011         1102.0                         Bonn Friedensplatz   
...                ...                                        ...   
3473714         1110.0                         Bonn Wilhelmsplatz   
3418794         1115.0  Bonn Bertha-Von-Suttner-Pl./Beethovenhaus   
3416876         1115.0  Bonn Bertha-Von-Suttner-Pl./Beethovenhaus   
3330682         1102.0                         Bonn Friedensplatz   
3402428         1500.0                 Bonn Konrad-Adenauer-Platz   

                                         start_buffer_zone  end_stop_id  \
3284125  801621     POLYGON ((7.157885983913106 50.7227...       1504.0   
2960244  801621     POLYGON ((7.157885983913106 50.7227...       1502.0   
3109531  801621     POLYGON ((7.157885983913106 50.7227...       1221.0   
2999342  801621     POLYGON ((7.157885983913106 50.7227...       1103.0   
3181011  801621     POLYGON ((7.157885983913106 50.7227...       1115.0   
...                                                    ...          ...   
3473714  801621     POLYGON ((7.157885983913106 50.7227...       1110.0   
3418794  801621     POLYGON ((7.157885983913106 50.7227...       1102.0   
3416876  801621     POLYGON ((7.157885983913106 50.7227...       1540.0   
3330682  801621     POLYGON ((7.157885983913106 50.7227...       1175.0   
3402428  801621     POLYGON ((7.157885983913106 50.7227...       8635.0   

                                     end_stop_name  \
3284125                              Bonn Beuel Bf   
2960244                 Bonn Beueler Bahnhofsplatz   
3109531                          Bonn Kaufmannstr.   
2999342                                 Bonn Markt   
3181011  Bonn Bertha-Von-Suttner-Pl./Beethovenhaus   
...                                            ...   
3473714                    

In [63]:
morning_rush_nan_delay_tier_station_station.describe()

tier_trips_id          tier_trips_start_time  \
count   5.960000e+02                            596   
mean    7.953060e+08  2023-07-14 01:57:31.510066944   
min     7.822651e+08            2023-07-01 06:25:00   
25%     7.823644e+08            2023-07-07 08:42:30   
50%     7.824462e+08            2023-07-12 09:05:00   
75%     8.087169e+08            2023-07-19 09:26:15   
max     8.323040e+08            2023-07-31 09:45:00   
std     1.532359e+07                            NaN   

                 tier_trips_end_time              trip_duration  \
count                            596                        596   
mean   2023-07-14 02:09:32.315436544  0 days 00:12:00.805369127   
min              2023-07-01 06:35:00            0 days 00:05:00   
25%              2023-07-07 08:52:30            0 days 00:10:00   
50%              2023-07-12 09:15:00            0 days 00:10:00   
75%              2023-07-19 09:45:00            0 days 00:15:00   
max              2023-07-31 09:55:00            0 days 01:40:00   
std                              NaN  0 days 00:07:13.671085956   

       trip_distance_kilometers  trip_distance_meters  start_stop_id  \
count                596.000000            596.000000     596.000000   
mean                   1.344135           1344.135332    1415.639262   
min                    0.105761            105.761295     161.000000   
25%                    0.638688            638.687532    1102.000000   
50%                    1.127895           1127.894611    1138.000000   
75%                    1.804931           1804.930612    1240.250000   
max                    7.493420           7493.420487    9703.000000   
std                    0.998249            998.248722    1428.311184   

       end_stop_id  trip_duration_seconds  
count   596.000000             596.000000  
mean   1274.491611             720.805369  
min      43.000000             300.000000  
25%    1102.000000             600.000000  
50%    1131.000000             600.000000  
75%    1221.000000             900.000000  
max    9780.000000            6000.000000  
std    1215.539169             433.671086

In [64]:
# get statistics for the tier trips that start and end at a station
get_stats(morning_rush_nan_delay_tier_station_station, ['trip_duration_seconds', 'trip_distance_kilometers'])

column                                     trip_duration_seconds  \
rows                                                         596   
sum                                                     429600.0   
mean                                                  720.805369   
median                                                     600.0   
mode           0    600.0
Name: trip_duration_seconds, dtype:...   
max                                                       6000.0   
min                                                        300.0   
std_dev                                               433.671086   
variance                                           188070.610795   
skewness                                                4.723339   
kurtosis                                               43.129337   
percentile_25                                              600.0   
percentile_75                                              900.0   
iqr                                                        300.0   
range                                                     5700.0   
cv                                                      0.601648   
qd                                                           0.2   
cs                                                      0.010892   
ck                                                      0.099452   
cvs                                                     0.010892   
cvk                                                     0.099452   
cvcs                                                    0.010892   
cvck                                                    0.099452   
cvcv                                                    0.601648   
cvqd                                                         0.2   
cvr                                                     7.907821   
cvm                                                          1.0   
cvmed                                                   0.832402   
cvmode         0    0.832402
Name: trip_duration_seconds, dty...   

column                                  trip_distance_kilometers  
rows                                                         596  
sum                                                   801.104658  
mean                                                    1.344135  
median                                                  1.127895  
mode           0      0.105761
1      0.106681
2      0.11000...  
max                                                      7.49342  
min                                                     0.105761  
std_dev                                                 0.998249  
variance                                                0.996501  
skewness                                                1.672666  
kurtosis                                                4.959731  
percentile_25                                           0.638688  
percentile_75                                           1.804931  
iqr                                                     1.166243  
range                                                   7.387659  
cv                                                       0.74267  
qd                                                      0.477261  
cs                                                      1.675601  
ck                                                      4.968432  
cvs                                                     1.675601  
cvk                                                     4.968432  
cvcs                                                    1.675601  
cvck                                                    4.968432  
cvcv                                                     0.74267  
cvqd                                                    0.477261  
cvr                                                     5.496217  
cvm                                                          1.0  
cvmed                                                   0.839123  
cvmode         0

In [65]:
morning_rush_nan_delay_next = check_micromobility_datasets('next', morning_rush_nan_delay)

In [66]:
morning_rush_nan_delay_next.describe()

nextbike_trips_id      nextbike_trips_start_time  \
count       4.678000e+03                           4678   
mean        3.793949e+07  2023-07-14 22:22:07.875160320   
min         3.771654e+07            2023-07-01 06:01:00   
25%         3.783005e+07            2023-07-07 08:16:00   
50%         3.794214e+07            2023-07-14 06:06:00   
75%         3.804677e+07            2023-07-21 06:31:00   
max         3.817170e+07            2023-07-31 09:56:00   
std         1.273033e+05                            NaN   

             nextbike_trips_end_time              trip_duration  \
count                           4678                       4678   
mean   2023-07-14 22:36:01.308251136  0 days 00:13:53.433091064   
min              2023-07-01 06:11:00            0 days 00:05:00   
25%              2023-07-07 08:31:00            0 days 00:10:00   
50%              2023-07-14 06:16:00            0 days 00:10:00   
75%              2023-07-21 06:41:00            0 days 00:15:00   
max              2023-07-31 11:56:00            0 days 02:00:00   
std                              NaN  0 days 00:08:53.559311335   

       trip_distance_kilometers  trip_distance_meters  start_stop_id  \
count               4678.000000           4678.000000    3727.000000   
mean                   1.666765           1666.764677    1176.371613   
min                    0.100004            100.003661      43.000000   
25%                    0.781110            781.109739     687.000000   
50%                    1.317464           1317.464193    1115.000000   
75%                    2.138634           2138.633614    1221.000000   
max                   13.551691          13551.691284    9780.000000   
std                    1.365593           1365.593058    1059.531292   

       end_stop_id  trip_duration_seconds  
count  2820.000000            4678.000000  
mean   1118.229433             833.433091  
min      43.000000             300.000000  
25%     687.000000             600.000000  
50%    1135.000000             600.000000  
75%    1221.000000             900.000000  
max    9703.000000            7200.000000  
std     824.050134             533.559311

In [67]:
get_stats(morning_rush_nan_delay_next, ['trip_duration_seconds', 'trip_distance_kilometers'])

column                                     trip_duration_seconds  \
rows                                                        4678   
sum                                                    3898800.0   
mean                                                  833.433091   
median                                                     600.0   
mode           0    600.0
Name: trip_duration_seconds, dtype:...   
max                                                       7200.0   
min                                                        300.0   
std_dev                                               533.559311   
variance                                           284685.538712   
skewness                                                4.215472   
kurtosis                                               28.951834   
percentile_25                                              600.0   
percentile_75                                              900.0   
iqr                                                        300.0   
range                                                     6900.0   
cv                                                      0.640195   
qd                                                           0.2   
cs                                                      0.007901   
ck                                                      0.054262   
cvs                                                     0.007901   
cvk                                                     0.054262   
cvcs                                                    0.007901   
cvck                                                    0.054262   
cvcv                                                    0.640195   
cvqd                                                         0.2   
cvr                                                     8.279009   
cvm                                                          1.0   
cvmed                                                   0.719914   
cvmode         0    0.719914
Name: trip_duration_seconds, dty...   

column                                  trip_distance_kilometers  
rows                                                        4678  
sum                                                  7797.125161  
mean                                                    1.666765  
median                                                  1.317464  
mode           0    0.834842
Name: trip_distance_kilometers, ...  
max                                                    13.551691  
min                                                     0.100004  
std_dev                                                 1.365593  
variance                                                1.864844  
skewness                                                  2.3789  
kurtosis                                                9.384884  
percentile_25                                            0.78111  
percentile_75                                           2.138634  
iqr                                                     1.357524  
range                                                  13.451688  
cv                                                      0.819308  
qd                                                      0.464946  
cs                                                      1.742027  
ck                                                      6.872387  
cvs                                                     1.742027  
cvk                                                     6.872387  
cvcs                                                    1.742027  
cvck                                                    6.872387  
cvcv                                                    0.819308  
cvqd                                                    0.464946  
cvr                                                     8.070538  
cvm                                                          1.0  
cvmed                                                   0.790432  
cvmode         0

In [68]:
# get entries where trips start and end at station
morning_rush_nan_delay_next_station_station = morning_rush_nan_delay_next[morning_rush_nan_delay_next['end_stop_id'].notna() & morning_rush_nan_delay_next['start_stop_id'].notna()]
morning_rush_nan_delay_next_station_station

nextbike_trips_id nextbike_trips_start_time nextbike_trips_end_time  \
1311817           37850625       2023-07-01 06:21:00     2023-07-01 06:36:00   
1433891           38006735       2023-07-01 06:21:00     2023-07-01 06:36:00   
1471081           38035639       2023-07-01 06:26:00     2023-07-01 06:41:00   
1269781           37830049       2023-07-01 06:31:00     2023-07-01 06:46:00   
1488023           38048406       2023-07-01 06:31:00     2023-07-01 06:41:00   
...                    ...                       ...                     ...   
1236020           37726688       2023-07-31 09:41:00     2023-07-31 09:56:00   
1463109           37974425       2023-07-31 09:46:00     2023-07-31 10:01:00   
1369123           37938091       2023-07-31 09:46:00     2023-07-31 09:56:00   
1419028           37963190       2023-07-31 09:51:00     2023-07-31 10:01:00   
1563208           38167336       2023-07-31 09:56:00     2023-07-31 11:56:00   

         nextbike_trips_start_at_station  nextbike_trips_end_at_station  \
1311817                            False                          False   
1433891                            False                          False   
1471081                            False                          False   
1269781                            False                          False   
1488023                            False                           True   
...                                  ...                            ...   
1236020                            False                          False   
1463109                            False                          False   
1369123                            False                          False   
1419028                            False                          False   
1563208                             True                           True   

        vehicle type   trip_duration  trip_distance_kilometers  \
1311817         bike 0 days 00:15:00                  1.284558   
1433891         bike 0 days 00:15:00                  1.550245   
1471081         bike 0 days 00:15:00                  1.898569   
1269781         bike 0 days 00:15:00                  1.402119   
1488023         bike 0 days 00:10:00                  0.313697   
...              ...             ...                       ...   
1236020         bike 0 days 00:15:00                  2.283296   
1463109         bike 0 days 00:15:00                  2.142474   
1369123         bike 0 days 00:10:00                  0.552211   
1419028         bike 0 days 00:10:00                  1.277644   
1563208         bike 0 days 02:00:00                  3.481091   

         trip_distance_meters  \
1311817           1284.557726   
1433891           1550.245342   
1471081           1898.568609   
1269781           1402.119138   
1488023            313.697078   
...                       ...   
1236020           2283.296059   
1463109           2142.474179   
1369123            552.210742   
1419028           1277.644211   
1563208           3481.090632   

                                            start_location  \
1311817  b'\x01\x01\x00\x00\x00}\xeb\xc3z\xa3f\x1c@}\xc...   
1433891  b'\x01\x01\x00\x00\x00\xa9lXSYT\x1c@\xb0\xe6\x...   
1471081  b'\x01\x01\x00\x00\x00\xbb\x99\xd1\x8f\x86c\x1...   
1269781  b'\x01\x01\x00\x00\x00N\xd1\x91\\\xfec\x1c@\xf...   
1488023  b'\x01\x01\x00\x00\x00\xd2\xc2e\x156c\x1c@\x8b...   
...                                                    ...   
1236020  b'\x01\x01\x00\x00\x00\xc8$#ga_\x1c@\xde\x1e\x...   
1463109  b'\x01\x01\x00\x00\x00\x97\x1a\xa1\x9f\xa9W\x1...   
1369123  b'\x01\x01\x00\x00\x00\xadK\x8d\xd0\xcfT\x1c@\...   
1419028  b'\x01\x01\x00\x00\x00qu\x00\xc4]]\x1c@F\xd3\x...   
1563208  b'\x01\x01\x00\x00\x00&\x199\x0b{Z\x1c@\xb4\xe...   

                                              end_location  start_stop_id  \
1311817  b'\x01\x01\x00\x00\x001\x08\xac\x1cZd\x1c@C\x9...         1160.0   
1433891  b'\x01\x01\x00\x00\x00\xdapX\x1a\xf8a\x1c@(\x0...

In [69]:
morning_rush_nan_delay_next_station_station.describe()

nextbike_trips_id      nextbike_trips_start_time  \
count       2.383000e+03                           2383   
mean        3.794132e+07  2023-07-14 21:26:58.816617728   
min         3.771654e+07            2023-07-01 06:21:00   
25%         3.783187e+07            2023-07-07 08:46:00   
50%         3.794202e+07            2023-07-13 09:46:00   
75%         3.804855e+07            2023-07-21 06:43:30   
max         3.817163e+07            2023-07-31 09:56:00   
std         1.275157e+05                            NaN   

             nextbike_trips_end_time              trip_duration  \
count                           2383                       2383   
mean   2023-07-14 21:39:55.719681280  0 days 00:12:56.903063365   
min              2023-07-01 06:36:00            0 days 00:05:00   
25%              2023-07-07 08:58:30            0 days 00:10:00   
50%              2023-07-13 10:01:00            0 days 00:10:00   
75%              2023-07-21 06:56:00            0 days 00:15:00   
max              2023-07-31 11:56:00            0 days 02:00:00   
std                              NaN  0 days 00:08:02.482013780   

       trip_distance_kilometers  trip_distance_meters  start_stop_id  \
count               2383.000000           2383.000000    2383.000000   
mean                   1.386574           1386.573807    1208.977339   
min                    0.100004            100.003661      43.000000   
25%                    0.728527            728.526920     687.000000   
50%                    1.192966           1192.966486    1131.000000   
75%                    1.804991           1804.991265    1221.000000   
max                    8.148248           8148.248419    9780.000000   
std                    0.980082            980.081868    1083.757830   

       end_stop_id  trip_duration_seconds  
count  2383.000000            2383.000000  
mean   1131.736467             776.903063  
min      43.000000             300.000000  
25%     687.000000             600.000000  
50%    1140.000000             600.000000  
75%    1221.000000             900.000000  
max    9703.000000            7200.000000  
std     806.441728             482.482014

In [70]:
# get statistics for the tier trips that start and end at a station
get_stats(morning_rush_nan_delay_next_station_station, ['trip_duration_seconds', 'trip_distance_kilometers'])

column                                     trip_duration_seconds  \
rows                                                        2383   
sum                                                    1851360.0   
mean                                                  776.903063   
median                                                     600.0   
mode           0    600.0
Name: trip_duration_seconds, dtype:...   
max                                                       7200.0   
min                                                        300.0   
std_dev                                               482.482014   
variance                                           232788.893622   
skewness                                                4.975325   
kurtosis                                               41.942241   
percentile_25                                              600.0   
percentile_75                                              900.0   
iqr                                                        300.0   
range                                                     6900.0   
cv                                                      0.621032   
qd                                                           0.2   
cs                                                      0.010312   
ck                                                       0.08693   
cvs                                                     0.010312   
cvk                                                      0.08693   
cvcs                                                    0.010312   
cvck                                                     0.08693   
cvcv                                                    0.621032   
cvqd                                                         0.2   
cvr                                                     8.881417   
cvm                                                          1.0   
cvmed                                                   0.772297   
cvmode         0    0.772297
Name: trip_duration_seconds, dty...   

column                                  trip_distance_kilometers  
rows                                                        2383  
sum                                                  3304.205381  
mean                                                    1.386574  
median                                                  1.192966  
mode           0    0.834842
Name: trip_distance_kilometers, ...  
max                                                     8.148248  
min                                                     0.100004  
std_dev                                                 0.980082  
variance                                                 0.96056  
skewness                                                1.759942  
kurtosis                                                4.996155  
percentile_25                                           0.728527  
percentile_75                                           1.804991  
iqr                                                     1.076464  
range                                                   8.048245  
cv                                                      0.706837  
qd                                                      0.424889  
cs                                                      1.795709  
ck                                                      5.097692  
cvs                                                     1.795709  
cvk                                                     5.097692  
cvcs                                                    1.795709  
cvck                                                    5.097692  
cvcv                                                    0.706837  
cvqd                                                    0.424889  
cvr                                                     5.804411  
cvm                                                          1.0  
cvmed                                                    0.86037  
cvmode         0

In [71]:
morning_rush_delay.describe()

route_id      agency_id     route_type     service_id  \
count  188742.000000  188742.000000  188742.000000  188742.000000   
mean      564.480349       6.004768       2.754506    3183.013632   
min        60.000000       6.000000       0.000000       3.000000   
25%       602.000000       6.000000       3.000000      64.000000   
50%       607.000000       6.000000       3.000000      64.000000   
75%       611.000000       6.000000       3.000000     130.000000   
max       843.000000      12.000000       3.000000   27690.000000   
std       152.455075       0.163342       0.822325    8571.218178   

        direction_id       shape_id        stop_id  \
count  188742.000000  188742.000000  188742.000000   
mean        0.527095    3556.255555    2369.052495   
min         0.000000       6.000000      43.000000   
25%         0.000000    1812.000000    1221.000000   
50%         1.000000    2717.000000    1441.000000   
75%         1.000000    5633.000000    1684.000000   
max         1.000000   10365.000000    9780.000000   
std         0.499267    2811.021692    2470.327951   

                 actual_arrival_time          actual_departure_time  \
count                         181761                         188742   
mean   2023-07-16 14:40:20.218996736  2023-07-16 15:20:27.515470592   
min              2023-07-01 06:00:00            2023-07-01 06:00:15   
25%              2023-07-08 09:42:30  2023-07-08 09:49:33.750000128   
50%              2023-07-17 08:10:00            2023-07-17 08:22:30   
75%              2023-07-24 09:08:30            2023-07-24 09:15:15   
max              2023-07-31 10:03:45            2023-07-31 10:03:45   
std                              NaN                            NaN   

       vrs_timestamp  ...  departure_delay_float actual_arrival_time_float  \
count  188742.000000  ...          188742.000000             188742.000000   
mean    65346.858993  ...               0.734455              75659.676304   
min     35805.000000  ...               0.000000                  0.000000   
25%     54803.000000  ...               0.250000              65800.000000   
50%     64305.000000  ...               0.500000              75800.000000   
75%     74804.000000  ...               0.750000              90315.000000   
max    133306.000000  ...             510.750000             152700.000000   
std     12215.263590  ...               6.844683              18526.082151   

      actual_departure_time_float arrival_delay_span    weather_int  \
count               188742.000000           188742.0  188742.000000   
mean                 78570.436919                0.0       0.188734   
min                  60010.000000                0.0       0.000000   
25%                  70515.000000                0.0       0.000000   
50%                  80245.000000                0.0       0.000000   
75%                  90515.000000                0.0       0.000000   
max                 152715.000000                0.0       2.000000   
std                  11297.520537                0.0       0.475514   

       time_span_int_arrival        weekend  time_span_int  delay_category  \
count          188742.000000  188742.000000  188742.000000   188742.000000   
mean                0.964677       0.611125       1.001600        0.623693   
min                 0.000000       0.000000       1.000000       -1.000000   
25%                 1.000000       0.000000       1.000000        0.000000   
50%                 1.000000       0.000000       1.000000        1.000000   
75%                 1.000000       1.000000       1.000000        1.000000   
max                 8.000000       3.000000       4.000000        1.000000   
std                 0.202473       0.940955       0.048036        0.555586   

       cancelled_trip  
count        188742.0  
mean              0.0  
min               0.0  
25%               0.0  
50%               0.0  
75%               0.0  
max               0.0  
std               0.0  



In [72]:
morning_rush_no_delay.describe()

route_id      agency_id     route_type     service_id  \
count  122186.000000  122186.000000  122186.000000  122186.000000   
mean      570.630318       7.021410       2.652972    5666.937243   
min        16.000000       1.000000       0.000000       3.000000   
25%       600.000000       6.000000       3.000000      64.000000   
50%       607.000000       6.000000       3.000000      64.000000   
75%       630.000000       6.000000       3.000000     151.000000   
max       884.000000      12.000000       3.000000   29145.000000   
std       209.201846       2.160208       0.959512   10976.279327   

        direction_id       shape_id        stop_id  \
count  122186.000000  122186.000000  122186.000000   
mean        0.494410    4163.839171    2134.628648   
min         0.000000       6.000000      43.000000   
25%         0.000000    1999.000000    1181.000000   
50%         0.000000    3091.000000    1406.000000   
75%         1.000000    6391.000000    1702.000000   
max         1.000000   10365.000000    9780.000000   
std         0.499971    2883.473279    2238.665907   

                 actual_arrival_time          actual_departure_time  \
count                          85348                         122186   
mean   2023-07-16 13:13:11.567113216  2023-07-16 14:32:50.248268800   
min              2023-07-01 05:59:00            2023-07-01 06:00:00   
25%              2023-07-08 09:27:30            2023-07-08 14:59:15   
50%              2023-07-17 08:04:45            2023-07-17 08:22:00   
75%              2023-07-24 08:42:45            2023-07-24 08:45:00   
max              2023-07-31 09:58:45            2023-07-31 09:59:30   
std                              NaN                            NaN   

       vrs_timestamp  ...  departure_delay_float actual_arrival_time_float  \
count  122186.000000  ...          122186.000000             122186.000000   
mean    65045.012776  ...               0.052844              54517.138707   
min     35805.000000  ...               0.000000                  0.000000   
25%     54305.000000  ...               0.000000                  0.000000   
50%     64304.000000  ...               0.000000              70930.000000   
75%     74305.000000  ...               0.000000              83245.000000   
max    220309.000000  ...             510.000000             100100.000000   
std     12170.493842  ...               1.535737              37034.566109   

      actual_departure_time_float arrival_delay_span    weather_int  \
count               122186.000000           122186.0  122186.000000   
mean                 78192.836454                0.0       0.193124   
min                  55900.000000                0.0       0.000000   
25%                  70300.000000                0.0       0.000000   
50%                  75930.000000                0.0       0.000000   
75%                  90100.000000                0.0       0.000000   
max                 143400.000000                0.0       2.000000   
std                  11208.103267                0.0       0.480259   

       time_span_int_arrival        weekend  time_span_int  delay_category  \
count          122186.000000  122186.000000  122186.000000    122186.00000   
mean                0.713134       0.603776       1.000426        -0.29568   
min                 0.000000       0.000000       1.000000        -1.00000   
25%                 0.000000       0.000000       1.000000        -1.00000   
50%                 1.000000       0.000000       1.000000         0.00000   
75%                 1.000000       1.000000       1.000000         0.00000   
max                 8.000000       3.000000       8.000000         1.00000   
std                 0.566992       0.937017       0.028027         0.46891   

       cancelled_trip  
count        122186.0  
mean              0.0  
min               0.0  
25%               0.0  
50%               0.0  
75%               0.0  
max               0.0  
std               0.0  



In [73]:
morning_rush_no_delay.describe()

route_id      agency_id     route_type     service_id  \
count  122186.000000  122186.000000  122186.000000  122186.000000   
mean      570.630318       7.021410       2.652972    5666.937243   
min        16.000000       1.000000       0.000000       3.000000   
25%       600.000000       6.000000       3.000000      64.000000   
50%       607.000000       6.000000       3.000000      64.000000   
75%       630.000000       6.000000       3.000000     151.000000   
max       884.000000      12.000000       3.000000   29145.000000   
std       209.201846       2.160208       0.959512   10976.279327   

        direction_id       shape_id        stop_id  \
count  122186.000000  122186.000000  122186.000000   
mean        0.494410    4163.839171    2134.628648   
min         0.000000       6.000000      43.000000   
25%         0.000000    1999.000000    1181.000000   
50%         0.000000    3091.000000    1406.000000   
75%         1.000000    6391.000000    1702.000000   
max         1.000000   10365.000000    9780.000000   
std         0.499971    2883.473279    2238.665907   

                 actual_arrival_time          actual_departure_time  \
count                          85348                         122186   
mean   2023-07-16 13:13:11.567113216  2023-07-16 14:32:50.248268800   
min              2023-07-01 05:59:00            2023-07-01 06:00:00   
25%              2023-07-08 09:27:30            2023-07-08 14:59:15   
50%              2023-07-17 08:04:45            2023-07-17 08:22:00   
75%              2023-07-24 08:42:45            2023-07-24 08:45:00   
max              2023-07-31 09:58:45            2023-07-31 09:59:30   
std                              NaN                            NaN   

       vrs_timestamp  ...  departure_delay_float actual_arrival_time_float  \
count  122186.000000  ...          122186.000000             122186.000000   
mean    65045.012776  ...               0.052844              54517.138707   
min     35805.000000  ...               0.000000                  0.000000   
25%     54305.000000  ...               0.000000                  0.000000   
50%     64304.000000  ...               0.000000              70930.000000   
75%     74305.000000  ...               0.000000              83245.000000   
max    220309.000000  ...             510.000000             100100.000000   
std     12170.493842  ...               1.535737              37034.566109   

      actual_departure_time_float arrival_delay_span    weather_int  \
count               122186.000000           122186.0  122186.000000   
mean                 78192.836454                0.0       0.193124   
min                  55900.000000                0.0       0.000000   
25%                  70300.000000                0.0       0.000000   
50%                  75930.000000                0.0       0.000000   
75%                  90100.000000                0.0       0.000000   
max                 143400.000000                0.0       2.000000   
std                  11208.103267                0.0       0.480259   

       time_span_int_arrival        weekend  time_span_int  delay_category  \
count          122186.000000  122186.000000  122186.000000    122186.00000   
mean                0.713134       0.603776       1.000426        -0.29568   
min                 0.000000       0.000000       1.000000        -1.00000   
25%                 0.000000       0.000000       1.000000        -1.00000   
50%                 1.000000       0.000000       1.000000         0.00000   
75%                 1.000000       1.000000       1.000000         0.00000   
max                 8.000000       3.000000       8.000000         1.00000   
std                 0.566992       0.937017       0.028027         0.46891   

       cancelled_trip  
count        122186.0  
mean              0.0  
min               0.0  
25%               0.0  
50%               0.0  
75%               0.0  
max               0.0  
std               0.0  



In [74]:
show_short_df(morning_rush_delay)

route_id                                            trip_id  stop_id  \
2651          606  6060003-606-006-1357.2.21:053800-42-1_4E8CA248...     1620   
2652          602  6020006-602-006-9478.2.22:055600-39-1_812F7A36...     1441   
2654          611  6110147-611-006-1723.2.21:055000-60-1_39D7C4D7...     1604   
2655          600  6000317-600-006-687.2.24:054500-16-1_7F8D7B79-...     1171   
2661          600  6000317-600-006-687.2.24:054500-16-1_7F8D7B79-...     1172   
...           ...                                                ...      ...   
2494915       633  6330028-633-006-1584.2.24:094300-24-1_5B1B51F9...     1500   
2494917       600  6000027-600-006-1308.2.21:092500-36-1_B8848C0F...     1115   
2494918       600  6000028-600-006-8813.2.22:095900-32-1_53EFFD6B...     8814   
2494919       601  6010051-601-006-1293.2.21:085900-46-1_5C215E86...      694   
2494925       610  6100057-610-006-1756.2.21:092600-54-1_FE6EB802...      692   

                                         stop_name scheduled_arrival_time  \
2651                           Bonn Max-Bruch-Str.    2023-07-01 06:00:00   
2652                           Bonn Chemnitzer Weg    2023-07-01 06:00:00   
2654                               Bonn Am Kurpark    2023-07-01 06:00:00   
2655                               Bonn Friesenweg    2023-07-01 06:00:00   
2661                               Bonn Bataverweg    2023-07-01 06:00:00   
...                                            ...                    ...   
2494915                 Bonn Konrad-Adenauer-Platz    2023-07-31 09:59:00   
2494917  Bonn Bertha-Von-Suttner-Pl./Beethovenhaus    2023-07-31 09:59:00   
2494918               Bonn Graurheindorf Hafen/Bwi    2023-07-31 09:59:00   
2494919                     Bonn Tannenbusch Mitte    2023-07-31 09:59:00   
2494925               Bonn Heussallee/Museumsmeile    2023-07-31 09:59:00   

        actual_arrival_time scheduled_departure_time actual_departure_time  \
2651    2023-07-01 06:00:30      2023-07-01 06:00:00   2023-07-01 06:00:45   
2652    2023-07-01 06:00:00      2023-07-01 06:00:00   2023-07-01 06:00:15   
2654    2023-07-01 06:00:00      2023-07-01 06:00:00   2023-07-01 06:00:15   
2655    2023-07-01 06:00:30      2023-07-01 06:00:00   2023-07-01 06:00:45   
2661    2023-07-01 06:00:00      2023-07-01 06:00:00   2023-07-01 06:00:15   
...                     ...                      ...                   ...   
2494915 2023-07-31 09:59:00      2023-07-31 09:59:00   2023-07-31 09:59:30   
2494917 2023-07-31 09:58:45      2023-07-31 09:59:00   2023-07-31 09:59:15   
2494918 2023-07-31 09:59:15      2023-07-31 09:59:00   2023-07-31 09:59:30   
2494919 2023-07-31 09:59:15      2023-07-31 09:59:00   2023-07-31 09:59:45   
2494925 2023-07-31 09:59:30      2023-07-31 09:59:00   2023-07-31 10:02:00   

          arrival_delay departure_delay  tier_trips_count  \
2651    0 days 00:00:30 0 days 00:00:45                 0   
2652    0 days 00:00:00 0 days 00:00:15                 0   
2654    0 days 00:00:00 0 days 00:00:15                 0   
2655    0 days 00:00:30 0 days 00:00:45                 0   
2661    0 days 00:00:00 0 days 00:00:15                 0   
...                 ...             ...               ...   
2494915 0 days 00:00:00 0 days 00:00:30                 0   
2494917 0 days 00:00:00 0 days 00:00:15                 0   
2494918 0 days 00:00:15 0 days 00:00:30                 0   
2494919 0 days 00:00:15 0 days 00:00:45                 0   
2494925 0 days 00:00:30 0 days 00:03:00                 0   

         tier_trips_end_at_station_count  nextbike_trips_count  \
2651                                   0                     0   
2652                                   0                     0   
2654                                   0                     0   
2655                                   0                     0   
2661                                   0                     0   
...                                  ...     

In [75]:
show_short_df(morning_rush_no_delay)

route_id                                            trip_id  stop_id  \
2657          608  6080121-608-006-687.2.26:053300-25-1_FAFFF268-...     1564   
2659          605  6050124-605-006-687.2.34:054200-19-1_BDBC7386-...     1344   
2672          611  6110003-611-006-1723.2.21:052000-60-1_65AA540D...      687   
2673          612  6120004-612-006-1280.2.22:055800-36-1_7F6838D0...     1285   
2675          606  6060004-606-006-1584.2.22:054000-44-1_9B6D17A0...     1103   
...           ...                                                ...      ...   
2494920       609  6090048-609-006-1574.2.24:091900-45-1_963E3448...     1141   
2494922       600  6000028-600-006-8813.2.22:095900-32-1_53EFFD6B...     8813   
2494924       601  6010061-601-006-1293.2.21:095900-46-1_44BE0AA0...     1293   
2494926       800  14-800-012-1690.2.22:092600-26-1_CD076C67-B58E...     1344   
2494927        65  651030-65-006-1406.1.12:094400-24-179_3601D3CC...     1115   

                                         stop_name scheduled_arrival_time  \
2657                              Bonn Heidebergen    2023-07-01 06:00:00   
2659                            Bonn Am Schickshof    2023-07-01 06:00:00   
2672                                      Bonn Hbf    2023-07-01 06:00:00   
2673                              Bonn Stephanstr.    2023-07-01 06:00:00   
2675                                    Bonn Markt    2023-07-01 06:00:00   
...                                            ...                    ...   
2494920                          Bonn Herwarthstr.    2023-07-31 09:59:00   
2494922                             Bonn Kranenweg    2023-07-31 09:59:00   
2494924                       Bonn Uniklinikum Süd    2023-07-31 09:59:00   
2494926                         Bonn Am Schickshof    2023-07-31 09:59:00   
2494927  Bonn Bertha-Von-Suttner-Pl./Beethovenhaus    2023-07-31 09:59:00   

        actual_arrival_time scheduled_departure_time actual_departure_time  \
2657    2023-07-01 05:59:45      2023-07-01 06:00:00   2023-07-01 06:00:00   
2659    2023-07-01 05:59:45      2023-07-01 06:00:00   2023-07-01 06:00:00   
2672    2023-07-01 05:59:00      2023-07-01 06:02:00   2023-07-01 06:02:00   
2673    2023-07-01 05:59:45      2023-07-01 06:00:00   2023-07-01 06:00:00   
2675    2023-07-01 05:59:45      2023-07-01 06:00:00   2023-07-01 06:00:00   
...                     ...                      ...                   ...   
2494920 2023-07-31 09:58:45      2023-07-31 09:59:00   2023-07-31 09:59:00   
2494922                 NaT      2023-07-31 09:59:00   2023-07-31 09:59:00   
2494924                 NaT      2023-07-31 09:59:00   2023-07-31 09:59:00   
2494926                 NaT      2023-07-31 09:59:00   2023-07-31 09:59:00   
2494927 2023-07-31 09:58:20      2023-07-31 09:59:00   2023-07-31 09:59:00   

        arrival_delay departure_delay  tier_trips_count  \
2657           0 days          0 days                 0   
2659           0 days          0 days                 0   
2672           0 days          0 days                 0   
2673           0 days          0 days                 0   
2675           0 days          0 days                 0   
...               ...             ...               ...   
2494920        0 days          0 days                 0   
2494922           NaT          0 days                 0   
2494924           NaT          0 days                 0   
2494926           NaT          0 days                 0   
2494927        0 days          0 days                 0   

         tier_trips_end_at_station_count  nextbike_trips_count  \
2657                                   0                     0   
2659                                   0                     0   
2672                                   0                     0   
2673                                   0                     0   
2675                                   0                     0   
...                                  ...                   ...   
249

In [76]:
show_short_df(morning_rush_nan_delay)

route_id                                            trip_id  stop_id  \
2653          610  6100003-610-006-1756.2.21:051000-54-1_22331419...     1336   
2656          610  6100005-610-006-1756.2.21:054000-54-1_942CB978...     1640   
2658          612  6120109-612-006-1763.2.21:053900-39-1_198A032D...     9477   
2660          600  6000218-600-006-8813.2.22:054000-38-1_76B49E18...     1134   
2662          604  6040003-604-006-1382.2.21:055600-49-1_37DB308A...     1313   
...           ...                                                ...      ...   
2494906       603  6030023-603-006-1386.2.21:091000-37-1_E15D6262...     2310   
2494913       609  6090060-609-006-1574.2.24:085900-45-1_EF291F3C...     1371   
2494921       605  6050025-605-006-1341.2.24:092600-40-1_BD980DE1...     1153   
2494923       540  5400021-540-006-687.2.23:094400-32-1_9099DD74-...     1514   
2494928       608  6080053-608-006-1374.2.21:092100-46-1_72BA3349...     1115   

                                         stop_name scheduled_arrival_time  \
2653                       Bonn Martin-Legros-Str.    2023-07-01 06:00:00   
2656                             Bonn Kennedyallee    2023-07-01 06:00:00   
2658              Bonn Bad Godesberg Bf / Löbestr.    2023-07-01 06:00:00   
2660                     Bonn Wilhelm-Levison-Str.    2023-07-01 06:00:00   
2662                       Bonn Lengsdorf Friedhof    2023-07-01 06:00:00   
...                                            ...                    ...   
2494906                          Bonn Zur Autobahn    2023-07-31 09:59:00   
2494913                Bonn Hardtberg Schulzentrum    2023-07-31 09:59:00   
2494921                              Bonn Heerstr.    2023-07-31 09:59:00   
2494923               Bonn Schwarzrheindorf Schule    2023-07-31 09:59:00   
2494928  Bonn Bertha-Von-Suttner-Pl./Beethovenhaus    2023-07-31 09:59:00   

        actual_arrival_time scheduled_departure_time actual_departure_time  \
2653                    NaT      2023-07-01 06:00:00                   NaT   
2656                    NaT      2023-07-01 06:00:00                   NaT   
2658                    NaT      2023-07-01 06:00:00                   NaT   
2660                    NaT      2023-07-01 06:00:00                   NaT   
2662                    NaT      2023-07-01 06:00:00                   NaT   
...                     ...                      ...                   ...   
2494906                 NaT      2023-07-31 09:59:00                   NaT   
2494913                 NaT      2023-07-31 09:59:00                   NaT   
2494921                 NaT      2023-07-31 09:59:00                   NaT   
2494923                 NaT      2023-07-31 09:59:00                   NaT   
2494928                 NaT      2023-07-31 09:59:00                   NaT   

        arrival_delay departure_delay  tier_trips_count  \
2653              NaT             NaT                 0   
2656              NaT             NaT                 0   
2658              NaT             NaT                 0   
2660              NaT             NaT                 0   
2662              NaT             NaT                 0   
...               ...             ...               ...   
2494906           NaT             NaT                 0   
2494913           NaT             NaT                 0   
2494921           NaT             NaT                 0   
2494923           NaT             NaT                 0   
2494928           NaT             NaT                 0   

         tier_trips_end_at_station_count  nextbike_trips_count  \
2653                                   0                     0   
2656                                   0                     0   
2658                                   0                     0   
2660                                   0                     0   
2662                                   0                     0   
...                                  ...                   ...   
249

#### Until Midday

In [77]:
midday_delay = delay[(delay['scheduled_arrival_time'].dt.hour > 9) & (delay['scheduled_arrival_time'].dt.hour < 12)]
midday_delay

route_id  agency_id route_short_name  route_type route_type_name  \
16913         640          6              640           3             Bus   
16915         611          6              611           3             Bus   
16917         600          6              600           3             Bus   
16918         610          6              610           3             Bus   
16923         603          6              603           3             Bus   
...           ...        ...              ...         ...             ...   
2505824        65          6               65           0            Tram   
2505826       604          6              604           3             Bus   
2505827       604          6              604           3             Bus   
2505834       636          6              636           3             Bus   
2505835       603          6              603           3             Bus   

                               agency_name  service_id  \
16913    SWB Stadtwerke Bonn Verkehrs GmbH         130   
16915    SWB Stadtwerke Bonn Verkehrs GmbH         130   
16917    SWB Stadtwerke Bonn Verkehrs GmbH         130   
16918    SWB Stadtwerke Bonn Verkehrs GmbH         130   
16923    SWB Stadtwerke Bonn Verkehrs GmbH         130   
...                                    ...         ...   
2505824  SWB Stadtwerke Bonn Verkehrs GmbH       26825   
2505826  SWB Stadtwerke Bonn Verkehrs GmbH          64   
2505827  SWB Stadtwerke Bonn Verkehrs GmbH          64   
2505834  SWB Stadtwerke Bonn Verkehrs GmbH          64   
2505835  SWB Stadtwerke Bonn Verkehrs GmbH          64   

                                                   trip_id  \
16913    6400603-640-006-687.2.23:095800-32-1_3A94BEA2-...   
16915    6110163-611-006-1723.2.21:092600-60-1_D1852C0B...   
16917    6000351-600-006-1308.2.21:092600-36-1_06A053AA...   
16918    6100137-610-006-1756.2.21:093900-54-1_D6C64451...   
16923    6030330-603-006-2304.2.22:095100-41-1_1C5599D8...   
...                                                    ...   
2505824  651031-65-006-1593.1.12:113400-24-179_18D71EB4...   
2505826  6040056-604-006-678.2.21:112300-51-1_BA8D6DCD-...   
2505827  6040054-604-006-678.2.21:110300-51-1_1C8F49B5-...   
2505834  6360031-636-006-1584.2.21:114600-19-1_68DB9A60...   
2505835  6030035-603-006-1386.2.21:111000-37-1_FF81A4AE...   

                trip_headsign  direction_id  ...  delay_span  \
16913             Siegburg Bf             0  ...         0-5   
16915    Lessenich Sportplatz             0  ...         0-5   
16917               Kranenweg             0  ...         0-5   
16918             Duisdorf Bf             0  ...         0-5   
16923        Röttgen Schleife             1  ...         0-5   
...                       ...           ...  ...         ...   
2505824     Kopenhagener Str.             0  ...         0-5   
2505826       Ückesdorf Mitte             1  ...         0-5   
2505827       Ückesdorf Mitte             1  ...         0-5   
2505834          Hangelar Ost             0  ...         0-5   
2505835        Alte Schulstr.             0  ...         0-5   

         arrival_delay_span weather_int time_span_arrival  \
16913                     0           1      until midday   
16915                     0           1      until midday   
16917                     0           1      until midday   
16918                     0           1      until midday   
16923                     0           1      until midday   
...                     ...         ...               ...   
2505824                   0           0                 0   
2505826                   0           0             lunch   
2505827                   0           0      until midday   
2505834                   0           0      until midday   
2505835                   0           0      until midday   

         time_span_int_arrival  weekend     time_span time_span_int  \
16913                        2        2  until midday             2  

In [78]:
get_stats(midday_delay, ['tier_trips_count', 'tier_trips_end_at_station_count', 'nextbike_trips_count', 'nextbike_trips_end_at_station_count', 'current_temp', 'current_precipitation_volume'])

/tmp/ipykernel_2575952/41814695.py:51: RuntimeWarning: invalid value encountered in scalar divide
  qd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:55: RuntimeWarning: invalid value encountered in scalar divide
  cvqd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:51: RuntimeWarning: invalid value encountered in scalar divide
  qd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:55: RuntimeWarning: invalid value encountered in scalar divide
  cvqd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:51: RuntimeWarning: invalid value encountered in scalar divide
  qd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:55: RuntimeWarning: invalid value encountered in scalar divide
  cvqd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:51: RuntimeWarning: invalid value encountered in scalar divide
  qd = iqr / (percentile_75 + percenti

column                                        tier_trips_count  \
rows                                                    101954   
sum                                                       1261   
mean                                                  0.012368   
median                                                     0.0   
mode               0    0
Name: tier_trips_count, dtype: int64   
max                                                          5   
min                                                          0   
std_dev                                               0.119807   
variance                                              0.014354   
skewness                                             11.946599   
kurtosis                                            206.389832   
percentile_25                                              0.0   
percentile_75                                              0.0   
iqr                                                        0.0   
range                                                        5   
cv                                                    9.686597   
qd                                                         NaN   
cs                                                   99.715404   
ck                                                 1722.686503   
cvs                                                  99.715404   
cvk                                                1722.686503   
cvcs                                                 99.715404   
cvck                                               1722.686503   
cvcv                                                  9.686597   
cvqd                                                       NaN   
cvr                                                 404.258525   
cvm                                                        1.0   
cvmed                                                      0.0   
cvmode         0    0.0
Name: tier_trips_count, dtype: float64   

column                           tier_trips_end_at_station_count  \
rows                                                      101954   
sum                                                         1034   
mean                                                    0.010142   
median                                                       0.0   
mode           0    0
Name: tier_trips_end_at_station_count, ...   
max                                                            5   
min                                                            0   
std_dev                                                 0.106368   
variance                                                0.011314   
skewness                                               12.248278   
kurtosis                                              206.522123   
percentile_25                                                0.0   
percentile_75                                                0.0   
iqr                                                          0.0   
range                                                          5   
cv                                                     10.488057   
qd                                                           NaN   
cs                                                    115.149943   
ck                                                   1941.579923   
cvs                                                   115.149943   
cvk                                                  1941.579923   
cvcs                                                  115.149943   
cvck                                                 1941.579923   
cvcv                                                   10.488057   
cvqd                                                         NaN   
cvr                                                   493.007737   
cvm                                                          1.0   
cvmed                                                        0.0   
cvmode         0    0.0
Name: tier_trips_end_at

In [79]:
midday_delay_tier = check_micromobility_datasets('tier', midday_delay)

In [80]:
midday_delay_tier.describe()

tier_trips_id       tier_trips_start_time  \
count   9.030000e+02                         903   
mean    7.969304e+08  2023-07-15 08:39:21.129568   
min     7.822653e+08         2023-07-01 10:05:00   
25%     7.823735e+08         2023-07-08 10:45:00   
50%     7.824642e+08         2023-07-13 11:55:00   
75%     8.087209e+08         2023-07-21 11:42:30   
max     8.323097e+08         2023-07-31 11:50:00   
std     1.555362e+07                         NaN   

                 tier_trips_end_time              trip_duration  \
count                            903                        903   
mean   2023-07-15 08:52:40.132890368  0 days 00:13:19.003322259   
min              2023-07-01 10:15:00            0 days 00:05:00   
25%              2023-07-08 10:55:00            0 days 00:10:00   
50%              2023-07-13 12:30:00            0 days 00:10:00   
75%              2023-07-21 11:57:30            0 days 00:15:00   
max              2023-07-31 12:40:00            0 days 01:35:00   
std                              NaN  0 days 00:08:58.999137136   

       trip_distance_kilometers  trip_distance_meters  start_stop_id  \
count                903.000000            903.000000     647.000000   
mean                   1.627277           1627.276791    1515.788253   
min                    0.100174            100.173813      43.000000   
25%                    0.639507            639.507264    1103.000000   
50%                    1.221489           1221.489338    1131.000000   
75%                    2.163888           2163.887551    1255.000000   
max                   13.908704          13908.703513    9703.000000   
std                    1.419126           1419.125821    1654.779991   

       end_stop_id  trip_duration_seconds  
count   546.000000             903.000000  
mean   1432.393773             799.003322  
min      43.000000             300.000000  
25%    1102.000000             600.000000  
50%    1152.500000             600.000000  
75%    1243.000000             900.000000  
max    9703.000000            5700.000000  
std    1567.365126             538.999137

In [81]:
get_stats(midday_delay_tier, ['trip_duration_seconds', 'trip_distance_kilometers'])

column                                     trip_duration_seconds  \
rows                                                         903   
sum                                                     721500.0   
mean                                                  799.003322   
median                                                     600.0   
mode           0    600.0
Name: trip_duration_seconds, dtype:...   
max                                                       5700.0   
min                                                        300.0   
std_dev                                               538.999137   
variance                                           290520.069834   
skewness                                                3.528018   
kurtosis                                               20.286545   
percentile_25                                              600.0   
percentile_75                                              900.0   
iqr                                                        300.0   
range                                                     5400.0   
cv                                                      0.674589   
qd                                                           0.2   
cs                                                      0.006545   
ck                                                      0.037637   
cvs                                                     0.006545   
cvk                                                     0.037637   
cvcs                                                    0.006545   
cvck                                                    0.037637   
cvcv                                                    0.674589   
cvqd                                                         0.2   
cvr                                                      6.75842   
cvm                                                          1.0   
cvmed                                                   0.750936   
cvmode         0    0.750936
Name: trip_duration_seconds, dty...   

column                                  trip_distance_kilometers  
rows                                                         903  
sum                                                  1469.430942  
mean                                                    1.627277  
median                                                  1.221489  
mode           0       0.100174
1       0.100631
2       0.10...  
max                                                    13.908704  
min                                                     0.100174  
std_dev                                                 1.419126  
variance                                                2.013918  
skewness                                                2.294357  
kurtosis                                                9.566031  
percentile_25                                           0.639507  
percentile_75                                           2.163888  
iqr                                                      1.52438  
range                                                   13.80853  
cv                                                      0.872086  
qd                                                      0.543762  
cs                                                       1.61674  
ck                                                      6.740791  
cvs                                                      1.61674  
cvk                                                     6.740791  
cvcs                                                     1.61674  
cvck                                                    6.740791  
cvcv                                                    0.872086  
cvqd                                                    0.543762  
cvr                                                     8.485667  
cvm                                                          1.0  
cvmed                                                   0.750634  
cvmode         0

In [82]:
# get entries where trips start and end at station
midday_delay_tier_station_station = midday_delay_tier[midday_delay_tier['end_stop_id'].notna() & midday_delay_tier['start_stop_id'].notna()]
midday_delay_tier_station_station

tier_trips_id tier_trips_start_time tier_trips_end_time vehicle type  \
3276328      782452113   2023-07-01 10:10:00 2023-07-01 10:30:00    e-scooter   
2943189      782276345   2023-07-01 10:10:00 2023-07-01 10:20:00    e-scooter   
3070408      782316392   2023-07-01 10:50:00 2023-07-01 11:00:00    e-scooter   
2917788      782268280   2023-07-01 11:15:00 2023-07-01 11:25:00    e-scooter   
3177165      782361066   2023-07-01 11:15:00 2023-07-01 11:25:00    e-scooter   
...                ...                   ...                 ...          ...   
3382781      832167178   2023-07-31 11:10:00 2023-07-31 11:20:00    e-scooter   
3520325      832299131   2023-07-31 11:15:00 2023-07-31 11:25:00    e-scooter   
3373057      832157820   2023-07-31 11:25:00 2023-07-31 11:35:00    e-scooter   
3349076      832140951   2023-07-31 11:30:00 2023-07-31 11:35:00    e-scooter   
3372204      832157070   2023-07-31 11:50:00 2023-07-31 12:00:00    e-scooter   

          trip_duration  trip_distance_kilometers  trip_distance_meters  \
3276328 0 days 00:20:00                  2.824580           2824.579934   
2943189 0 days 00:10:00                  1.122014           1122.013704   
3070408 0 days 00:10:00                  0.321411            321.411342   
2917788 0 days 00:10:00                  1.094055           1094.054859   
3177165 0 days 00:10:00                  0.328528            328.527835   
...                 ...                       ...                   ...   
3382781 0 days 00:10:00                  1.451136           1451.136461   
3520325 0 days 00:10:00                  0.791822            791.821871   
3373057 0 days 00:10:00                  0.852439            852.439337   
3349076 0 days 00:05:00                  0.315999            315.999193   
3372204 0 days 00:10:00                  0.801608            801.607929   

         start_stop_id                            start_stop_name  \
3276328         1234.0                      Bonn Am Klostergarten   
2943189         1115.0  Bonn Bertha-Von-Suttner-Pl./Beethovenhaus   
3070408         1102.0                         Bonn Friedensplatz   
2917788         8506.0                             Bonn Werftstr.   
3177165         1115.0  Bonn Bertha-Von-Suttner-Pl./Beethovenhaus   
...                ...                                        ...   
3382781         1302.0                     Bonn Ippendorfer Allee   
3520325         1502.0                 Bonn Beueler Bahnhofsplatz   
3373057         1140.0                            Bonn Mozartstr.   
3349076         1115.0  Bonn Bertha-Von-Suttner-Pl./Beethovenhaus   
3372204         1502.0                 Bonn Beueler Bahnhofsplatz   

                                         start_buffer_zone  end_stop_id  \
3276328  801621     POLYGON ((7.157885983913106 50.7227...        687.0   
2943189  801621     POLYGON ((7.157885983913106 50.7227...       1153.0   
3070408  801621     POLYGON ((7.157885983913106 50.7227...       1115.0   
2917788  801621     POLYGON ((7.157885983913106 50.7227...       1172.0   
3177165  801621     POLYGON ((7.157885983913106 50.7227...       1111.0   
...                                                    ...          ...   
3382781  801621     POLYGON ((7.157885983913106 50.7227...       1310.0   
3520325  801621     POLYGON ((7.157885983913106 50.7227...       1513.0   
3373057  801621     POLYGON ((7.157885983913106 50.7227...        687.0   
3349076  801621     POLYGON ((7.157885983913106 50.7227...       1102.0   
3372204  801621     POLYGON ((7.157885983913106 50.7227...       1500.0   

                                     end_stop_name  \
3276328                                   Bonn Hbf   
2943189                              Bonn Heerstr.   
3070408  Bonn Bertha-Von-Suttner-Pl./Beethovenhaus   
2917788                            Bonn Bataverweg   
3177165                Bonn Beethovenhalle Und Swb   
...                                            ...   
3382781                    

In [83]:
midday_delay_tier_station_station.describe()

tier_trips_id       tier_trips_start_time  \
count   4.490000e+02                         449   
mean    7.958960e+08  2023-07-15 02:48:42.494432   
min     7.822653e+08         2023-07-01 10:10:00   
25%     7.823817e+08         2023-07-08 10:45:00   
50%     7.824583e+08         2023-07-13 11:00:00   
75%     8.087142e+08         2023-07-21 11:20:00   
max     8.323097e+08         2023-07-31 11:50:00   
std     1.529130e+07                         NaN   

                 tier_trips_end_time              trip_duration  \
count                            449                        449   
mean   2023-07-15 03:00:43.429844224  0 days 00:12:00.935412026   
min              2023-07-01 10:20:00            0 days 00:05:00   
25%              2023-07-08 10:55:00            0 days 00:10:00   
50%              2023-07-13 11:20:00            0 days 00:10:00   
75%              2023-07-21 11:30:00            0 days 00:15:00   
max              2023-07-31 12:00:00            0 days 00:55:00   
std                              NaN  0 days 00:06:43.398528816   

       trip_distance_kilometers  trip_distance_meters  start_stop_id  \
count                449.000000            449.000000     449.000000   
mean                   1.353284           1353.283819    1580.550111   
min                    0.100174            100.173813      43.000000   
25%                    0.565112            565.111924    1103.000000   
50%                    1.031166           1031.166492    1131.000000   
75%                    1.869550           1869.550098    1240.000000   
max                    5.863966           5863.965941    9703.000000   
std                    1.078027           1078.026796    1777.903451   

       end_stop_id  trip_duration_seconds  
count   449.000000             449.000000  
mean   1460.064588             720.935412  
min      43.000000             300.000000  
25%    1106.000000             600.000000  
50%    1161.000000             600.000000  
75%    1243.000000             900.000000  
max    9703.000000            3300.000000  
std    1571.327161             403.398529

In [84]:
# get statistics for the tier trips that start and end at a station
get_stats(midday_delay_tier_station_station, ['trip_duration_seconds', 'trip_distance_kilometers'])

column                                     trip_duration_seconds  \
rows                                                         449   
sum                                                     323700.0   
mean                                                  720.935412   
median                                                     600.0   
mode           0    600.0
Name: trip_duration_seconds, dtype:...   
max                                                       3300.0   
min                                                        300.0   
std_dev                                               403.398529   
variance                                           162730.373051   
skewness                                                2.572887   
kurtosis                                               11.784188   
percentile_25                                              600.0   
percentile_75                                              900.0   
iqr                                                        300.0   
range                                                     3000.0   
cv                                                      0.559549   
qd                                                           0.2   
cs                                                      0.006378   
ck                                                      0.029212   
cvs                                                     0.006378   
cvk                                                     0.029212   
cvcs                                                    0.006378   
cvck                                                    0.029212   
cvcv                                                    0.559549   
cvqd                                                         0.2   
cvr                                                      4.16126   
cvm                                                          1.0   
cvmed                                                   0.832252   
cvmode         0    0.832252
Name: trip_duration_seconds, dty...   

column                                  trip_distance_kilometers  
rows                                                         449  
sum                                                   607.624435  
mean                                                    1.353284  
median                                                  1.031166  
mode           0      0.100174
1      0.100631
2      0.10540...  
max                                                     5.863966  
min                                                     0.100174  
std_dev                                                 1.078027  
variance                                                1.162142  
skewness                                                 1.42942  
kurtosis                                                2.239712  
percentile_25                                           0.565112  
percentile_75                                            1.86955  
iqr                                                     1.304438  
range                                                   5.763792  
cv                                                      0.796601  
qd                                                      0.535778  
cs                                                       1.32596  
ck                                                      2.077603  
cvs                                                      1.32596  
cvk                                                     2.077603  
cvcs                                                     1.32596  
cvck                                                    2.077603  
cvcv                                                    0.796601  
cvqd                                                    0.535778  
cvr                                                     4.259116  
cvm                                                          1.0  
cvmed                                                   0.761974  
cvmode         0

In [85]:
midday_delay_next = check_micromobility_datasets('next', midday_delay)

In [86]:
midday_delay_next.describe()

nextbike_trips_id      nextbike_trips_start_time  \
count       2.568000e+03                           2568   
mean        3.794197e+07  2023-07-15 07:34:38.107476480   
min         3.771660e+07            2023-07-01 10:01:00   
25%         3.782976e+07            2023-07-07 11:31:00   
50%         3.794438e+07            2023-07-14 10:51:00   
75%         3.804882e+07            2023-07-22 10:36:00   
max         3.817162e+07            2023-07-31 11:56:00   
std         1.281984e+05                            NaN   

             nextbike_trips_end_time              trip_duration  \
count                           2568                       2568   
mean   2023-07-15 07:48:49.976635648  0 days 00:14:11.869158878   
min              2023-07-01 10:16:00            0 days 00:05:00   
25%              2023-07-07 11:46:00            0 days 00:10:00   
50%              2023-07-14 11:03:30            0 days 00:10:00   
75%              2023-07-22 10:46:00            0 days 00:15:00   
max              2023-07-31 12:31:00            0 days 02:00:00   
std                              NaN  0 days 00:09:58.358691342   

       trip_distance_kilometers  trip_distance_meters  start_stop_id  \
count               2568.000000           2568.000000    1906.000000   
mean                   1.587309           1587.309139    1253.982162   
min                    0.100723            100.722819      43.000000   
25%                    0.678791            678.790868     687.000000   
50%                    1.188221           1188.221224    1115.000000   
75%                    2.074474           2074.474197    1223.000000   
max                   12.565163          12565.162585    9780.000000   
std                    1.396188           1396.188092    1232.943586   

       end_stop_id  trip_duration_seconds  
count  1593.000000            2568.000000  
mean   1288.475832             851.869159  
min      43.000000             300.000000  
25%     688.000000             600.000000  
50%    1140.000000             600.000000  
75%    1221.000000             900.000000  
max    9780.000000            7200.000000  
std    1385.990314             598.358691

In [87]:
get_stats(midday_delay_next, ['trip_duration_seconds', 'trip_distance_kilometers'])

column                                     trip_duration_seconds  \
rows                                                        2568   
sum                                                    2187600.0   
mean                                                  851.869159   
median                                                     600.0   
mode           0    600.0
Name: trip_duration_seconds, dtype:...   
max                                                       7200.0   
min                                                        300.0   
std_dev                                               598.358691   
variance                                           358033.123505   
skewness                                                 4.16133   
kurtosis                                               27.488922   
percentile_25                                              600.0   
percentile_75                                              900.0   
iqr                                                        300.0   
range                                                     6900.0   
cv                                                      0.702407   
qd                                                           0.2   
cs                                                      0.006955   
ck                                                      0.045941   
cvs                                                     0.006955   
cvk                                                     0.045941   
cvcs                                                    0.006955   
cvck                                                    0.045941   
cvcv                                                    0.702407   
cvqd                                                         0.2   
cvr                                                     8.099835   
cvm                                                          1.0   
cvmed                                                   0.704334   
cvmode         0    0.704334
Name: trip_duration_seconds, dty...   

column                                  trip_distance_kilometers  
rows                                                        2568  
sum                                                   4076.20987  
mean                                                    1.587309  
median                                                  1.188221  
mode           0    0.834842
Name: trip_distance_kilometers, ...  
max                                                    12.565163  
min                                                     0.100723  
std_dev                                                 1.396188  
variance                                                1.949341  
skewness                                                2.613809  
kurtosis                                               11.424719  
percentile_25                                           0.678791  
percentile_75                                           2.074474  
iqr                                                     1.395683  
range                                                   12.46444  
cv                                                      0.879594  
qd                                                      0.506919  
cs                                                      1.872104  
ck                                                      8.182794  
cvs                                                     1.872104  
cvk                                                     8.182794  
cvcs                                                    1.872104  
cvck                                                    8.182794  
cvcv                                                    0.879594  
cvqd                                                    0.506919  
cvr                                                      7.85256  
cvm                                                          1.0  
cvmed                                                   0.748576  
cvmode         0

In [88]:
# get entries where trips start and end at station
midday_delay_next_station_station = midday_delay_next[midday_delay_next['end_stop_id'].notna() & midday_delay_next['start_stop_id'].notna()]
midday_delay_next_station_station

nextbike_trips_id nextbike_trips_start_time nextbike_trips_end_time  \
1438661           38010471       2023-07-01 10:11:00     2023-07-01 10:21:00   
1529745           38081789       2023-07-01 10:11:00     2023-07-01 10:21:00   
1279079           37867245       2023-07-01 10:11:00     2023-07-01 10:21:00   
1398081           37952665       2023-07-01 10:11:00     2023-07-01 10:46:00   
1646587           37778006       2023-07-01 10:21:00     2023-07-01 10:31:00   
...                    ...                       ...                     ...   
1569214           38116283       2023-07-31 11:51:00     2023-07-31 11:56:00   
1624931           38158665       2023-07-31 11:56:00     2023-07-31 12:06:00   
1453284           38021980       2023-07-31 11:56:00     2023-07-31 12:01:00   
1523413           38076520       2023-07-31 11:56:00     2023-07-31 12:01:00   
1306881           37881127       2023-07-31 11:56:00     2023-07-31 12:01:00   

         nextbike_trips_start_at_station  nextbike_trips_end_at_station  \
1438661                            False                          False   
1529745                            False                          False   
1279079                            False                          False   
1398081                            False                          False   
1646587                            False                          False   
...                                  ...                            ...   
1569214                            False                          False   
1624931                            False                          False   
1453284                            False                          False   
1523413                            False                          False   
1306881                            False                          False   

        vehicle type   trip_duration  trip_distance_kilometers  \
1438661         bike 0 days 00:10:00                  0.931129   
1529745         bike 0 days 00:10:00                  1.254430   
1279079         bike 0 days 00:10:00                  0.704044   
1398081         bike 0 days 00:35:00                  1.716484   
1646587         bike 0 days 00:10:00                  1.381387   
...              ...             ...                       ...   
1569214         bike 0 days 00:05:00                  0.499254   
1624931         bike 0 days 00:10:00                  1.913166   
1453284         bike 0 days 00:05:00                  0.535144   
1523413         bike 0 days 00:05:00                  0.936625   
1306881         bike 0 days 00:05:00                  0.601569   

         trip_distance_meters  \
1438661            931.128902   
1529745           1254.430410   
1279079            704.043790   
1398081           1716.483636   
1646587           1381.386740   
...                       ...   
1569214            499.253733   
1624931           1913.166464   
1453284            535.144175   
1523413            936.625242   
1306881            601.568985   

                                            start_location  \
1438661  b'\x01\x01\x00\x00\x00!\xae\x9c\xbd3z\x1c@\xea...   
1529745  b'\x01\x01\x00\x00\x00H\xf9I\xb5OW\x1c@\x88\xd...   
1279079  b'\x01\x01\x00\x00\x00\xd9\xed\xb3\xcaLi\x1c@J...   
1398081  b'\x01\x01\x00\x00\x00\xbf\xeet\xe7\x89w\x1c@\...   
1646587  b'\x01\x01\x00\x00\x00\x81\xcc\xce\xa2wZ\x1c@w...   
...                                                    ...   
1569214  b'\x01\x01\x00\x00\x00\xf7\x90\xf0\xbd\xbfa\x1...   
1624931  b'\x01\x01\x00\x00\x00\xd6o&\xa6\x0bQ\x1c@m\xf...   
1453284  b"\x01\x01\x00\x00\x00\x86\x01K\xaeba\x1c@\x1b...   
1523413  b'\x01\x01\x00\x00\x00\x1c\xee#\xb7&m\x1c@\xaf...   
1306881  b'\x01\x01\x00\x00\x00\xf6\x085C\xaa(\x1c@\xa0...   

                                              end_location  start_stop_id  \
1438661  b'\x01\x01\x00\x00\x00?n\xbf|\xb2\x82\x1c@\x92...         1500.0   
1529745  b'\x01\x01\x00\x00\x00:\x94\xa1*\xa6b\x1c@A}\x...

In [89]:
midday_delay_next_station_station.describe()

nextbike_trips_id      nextbike_trips_start_time  \
count       1.294000e+03                           1294   
mean        3.794508e+07  2023-07-15 08:00:49.567233280   
min         3.771660e+07            2023-07-01 10:11:00   
25%         3.783461e+07            2023-07-07 11:36:00   
50%         3.794771e+07            2023-07-14 10:31:00   
75%         3.805070e+07            2023-07-22 10:16:00   
max         3.816994e+07            2023-07-31 11:56:00   
std         1.280904e+05                            NaN   

             nextbike_trips_end_time              trip_duration  \
count                           1294                       1294   
mean   2023-07-15 08:13:38.809891840  0 days 00:12:49.242658423   
min              2023-07-01 10:21:00            0 days 00:05:00   
25%              2023-07-07 11:46:00            0 days 00:10:00   
50%              2023-07-14 10:46:00            0 days 00:10:00   
75%              2023-07-22 10:31:00            0 days 00:15:00   
max              2023-07-31 12:31:00            0 days 01:35:00   
std                              NaN  0 days 00:07:47.220854623   

       trip_distance_kilometers  trip_distance_meters  start_stop_id  \
count               1294.000000           1294.000000    1294.000000   
mean                   1.299889           1299.889337    1247.836167   
min                    0.100723            100.722819      43.000000   
25%                    0.640588            640.588278     692.000000   
50%                    1.018467           1018.467488    1115.000000   
75%                    1.674456           1674.455881    1223.000000   
max                    7.527409           7527.409078    9702.000000   
std                    0.999422            999.422096    1205.077436   

       end_stop_id  trip_duration_seconds  
count  1294.000000            1294.000000  
mean   1333.806801             769.242658  
min      43.000000             300.000000  
25%     689.000000             600.000000  
50%    1140.000000             600.000000  
75%    1221.000000             900.000000  
max    9780.000000            5700.000000  
std    1475.926957             467.220855

In [90]:
# get statistics for the tier trips that start and end at a station
get_stats(midday_delay_next_station_station, ['trip_duration_seconds', 'trip_distance_kilometers'])

column                                     trip_duration_seconds  \
rows                                                        1294   
sum                                                     995400.0   
mean                                                  769.242658   
median                                                     600.0   
mode           0    600.0
Name: trip_duration_seconds, dtype:...   
max                                                       5700.0   
min                                                        300.0   
std_dev                                               467.220855   
variance                                           218295.326996   
skewness                                                3.606492   
kurtosis                                               22.413305   
percentile_25                                              600.0   
percentile_75                                              900.0   
iqr                                                        300.0   
range                                                     5400.0   
cv                                                      0.607378   
qd                                                           0.2   
cs                                                      0.007719   
ck                                                      0.047972   
cvs                                                     0.007719   
cvk                                                     0.047972   
cvcs                                                    0.007719   
cvck                                                    0.047972   
cvcv                                                    0.607378   
cvqd                                                         0.2   
cvr                                                     7.019892   
cvm                                                          1.0   
cvmed                                                   0.779988   
cvmode         0    0.779988
Name: trip_duration_seconds, dty...   

column                                  trip_distance_kilometers  
rows                                                        1294  
sum                                                  1682.056802  
mean                                                    1.299889  
median                                                  1.018467  
mode           0    0.834842
Name: trip_distance_kilometers, ...  
max                                                     7.527409  
min                                                     0.100723  
std_dev                                                 0.999422  
variance                                                0.998845  
skewness                                                2.066947  
kurtosis                                                6.888324  
percentile_25                                           0.640588  
percentile_75                                           1.674456  
iqr                                                     1.033868  
range                                                   7.426686  
cv                                                      0.768852  
qd                                                      0.446587  
cs                                                      2.068142  
ck                                                      6.892307  
cvs                                                     2.068142  
cvk                                                     6.892307  
cvcs                                                    2.068142  
cvck                                                    6.892307  
cvcv                                                    0.768852  
cvqd                                                    0.446587  
cvr                                                     5.713322  
cvm                                                          1.0  
cvmed                                                   0.783503  
cvmode         0

In [91]:
midday_no_delay = no_delay[(no_delay['scheduled_arrival_time'].dt.hour > 9) & (no_delay['scheduled_arrival_time'].dt.hour < 12)]
midday_no_delay

route_id  agency_id route_short_name  route_type route_type_name  \
16925         609          6              609           3             Bus   
16926         608          6              608           3             Bus   
16927         603          6              603           3             Bus   
16928         607          6              607           3             Bus   
16945         640          6              640           3             Bus   
...           ...        ...              ...         ...             ...   
2505824        65          6               65           0            Tram   
2505825       884         12              884           3             Bus   
2505828        63          6               63           0            Tram   
2505829       601          6              601           3             Bus   
2505831       636          6              636           3             Bus   

                                         agency_name  service_id  \
16925              SWB Stadtwerke Bonn Verkehrs GmbH         130   
16926              SWB Stadtwerke Bonn Verkehrs GmbH         130   
16927              SWB Stadtwerke Bonn Verkehrs GmbH         130   
16928              SWB Stadtwerke Bonn Verkehrs GmbH         130   
16945              SWB Stadtwerke Bonn Verkehrs GmbH         130   
...                                              ...         ...   
2505824            SWB Stadtwerke Bonn Verkehrs GmbH       26825   
2505825  RVK Regionalverkehr Köln GmbH NL Meckenheim       27690   
2505828            SWB Stadtwerke Bonn Verkehrs GmbH          43   
2505829            SWB Stadtwerke Bonn Verkehrs GmbH          64   
2505831            SWB Stadtwerke Bonn Verkehrs GmbH          64   

                                                   trip_id  \
16925    6090143-609-006-1374.2.21:093200-46-1_DB9595F1...   
16926    6080140-608-006-1574.2.24:092900-47-1_40D346B9...   
16927    6030328-603-006-2304.2.22:093100-41-1_D28C5CDA...   
16928    6070141-607-006-1357.2.21:091100-45-1_CAA7459E...   
16945    6400636-640-006-1811.2.25:093600-33-1_D983391D...   
...                                                    ...   
2505824  651031-65-006-1593.1.12:113400-24-179_18D71EB4...   
2505825  26-884-012-3332.2.22:115100-16-1_708966D9-1113...   
2505828  630025-63-006-371.1.11:115500-18-1_B3AAB150-CD...   
2505829  6010081-601-006-1293.2.21:115900-46-1_8673F26D...   
2505831  6360031-636-006-1584.2.21:114600-19-1_68DB9A60...   

                trip_headsign  direction_id  ...  delay_span  \
16925                 Gielgen             0  ...         0-5   
16926      Hardthöhe/Südwache             1  ...           0   
16927        Röttgen Schleife             1  ...           0   
16928              Ramersdorf             0  ...           0   
16945                Bonn Hbf             1  ...           0   
...                       ...           ...  ...         ...   
2505824     Kopenhagener Str.             0  ...         0-5   
2505825  Lessenich Sportplatz             1  ...           0   
2505828     Tannenbusch Mitte             0  ...           0   
2505829    Agnetendorfer Str.             0  ...           0   
2505831          Hangelar Ost             0  ...           0   

         arrival_delay_span weather_int time_span_arrival  \
16925                     0           1      until midday   
16926                     0           1      morning rush   
16927                     0           1                 0   
16928                     0           1      morning rush   
16945                     0           1      morning rush   
...                     ...         ...               ...   
2505824                   0           0                 0   
2505825                   0           0      until midday   
2505828                   0           0      until midday   
2505829                   0           0                 0   
2505831                   0           0      until midday   

         time_span_i

In [92]:
get_stats(midday_no_delay, ['tier_trips_count', 'tier_trips_end_at_station_count', 'nextbike_trips_count', 'nextbike_trips_end_at_station_count', 'current_temp', 'current_precipitation_volume'])

/tmp/ipykernel_2575952/41814695.py:51: RuntimeWarning: invalid value encountered in scalar divide
  qd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:55: RuntimeWarning: invalid value encountered in scalar divide
  cvqd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:51: RuntimeWarning: invalid value encountered in scalar divide
  qd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:55: RuntimeWarning: invalid value encountered in scalar divide
  cvqd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:51: RuntimeWarning: invalid value encountered in scalar divide
  qd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:55: RuntimeWarning: invalid value encountered in scalar divide
  cvqd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:51: RuntimeWarning: invalid value encountered in scalar divide
  qd = iqr / (percentile_75 + percenti

column                                        tier_trips_count  \
rows                                                     64182   
sum                                                       1792   
mean                                                  0.027921   
median                                                     0.0   
mode               0    0
Name: tier_trips_count, dtype: int64   
max                                                          5   
min                                                          0   
std_dev                                               0.185142   
variance                                              0.034278   
skewness                                              7.936123   
kurtosis                                             80.640162   
percentile_25                                              0.0   
percentile_75                                              0.0   
iqr                                                        0.0   
range                                                        5   
cv                                                    6.631015   
qd                                                         NaN   
cs                                                    42.86508   
ck                                                  435.558623   
cvs                                                   42.86508   
cvk                                                 435.558623   
cvcs                                                  42.86508   
cvck                                                435.558623   
cvcv                                                  6.631015   
cvqd                                                       NaN   
cvr                                                 179.079241   
cvm                                                        1.0   
cvmed                                                      0.0   
cvmode         0    0.0
Name: tier_trips_count, dtype: float64   

column                           tier_trips_end_at_station_count  \
rows                                                       64182   
sum                                                         1429   
mean                                                    0.022265   
median                                                       0.0   
mode           0    0
Name: tier_trips_end_at_station_count, ...   
max                                                            4   
min                                                            0   
std_dev                                                 0.162807   
variance                                                0.026506   
skewness                                                8.494729   
kurtosis                                               88.431105   
percentile_25                                                0.0   
percentile_75                                                0.0   
iqr                                                          0.0   
range                                                          4   
cv                                                      7.312289   
qd                                                           NaN   
cs                                                      52.17677   
ck                                                    543.166156   
cvs                                                     52.17677   
cvk                                                   543.166156   
cvcs                                                    52.17677   
cvck                                                  543.166156   
cvcv                                                    7.312289   
cvqd                                                         NaN   
cvr                                                   179.655703   
cvm                                                          1.0   
cvmed                                                        0.0   
cvmode         0    0.0
Name: tier_trips_end_at

In [93]:
midday_no_delay_tier = check_micromobility_datasets('tier', midday_no_delay)

In [94]:
midday_no_delay_tier.describe()

tier_trips_id          tier_trips_start_time  \
count   7.320000e+02                            732   
mean    7.966197e+08  2023-07-14 21:48:00.737704960   
min     7.822651e+08            2023-07-01 10:05:00   
25%     7.823779e+08            2023-07-07 10:25:00   
50%     7.824550e+08            2023-07-13 10:22:30   
75%     8.087385e+08            2023-07-22 11:00:00   
max     8.323066e+08            2023-07-31 11:55:00   
std     1.624794e+07                            NaN   

                 tier_trips_end_time              trip_duration  \
count                            732                        732   
mean   2023-07-14 22:02:02.950819584  0 days 00:14:02.213114754   
min              2023-07-01 10:20:00            0 days 00:05:00   
25%              2023-07-07 10:38:45            0 days 00:10:00   
50%              2023-07-13 10:37:30            0 days 00:10:00   
75%              2023-07-22 11:11:15            0 days 00:15:00   
max              2023-07-31 12:20:00            0 days 01:25:00   
std                              NaN  0 days 00:09:14.333277641   

       trip_distance_kilometers  trip_distance_meters  start_stop_id  \
count                732.000000            732.000000     581.000000   
mean                   1.687177           1687.176560    1233.096386   
min                    0.100174            100.173813      43.000000   
25%                    0.665587            665.587082     687.000000   
50%                    1.301309           1301.308623    1115.000000   
75%                    2.171730           2171.729601    1406.000000   
max                    9.215283           9215.283180    9702.000000   
std                    1.412409           1412.408995    1202.370054   

       end_stop_id  trip_duration_seconds  
count   396.000000             732.000000  
mean   1436.800505             842.213115  
min      43.000000             300.000000  
25%    1102.000000             600.000000  
50%    1150.500000             600.000000  
75%    1224.000000             900.000000  
max    9780.000000            5100.000000  
std    1579.046640             554.333278

In [95]:
get_stats(midday_no_delay_tier, ['trip_duration_seconds', 'trip_distance_kilometers'])

column                                     trip_duration_seconds  \
rows                                                         732   
sum                                                     616500.0   
mean                                                  842.213115   
median                                                     600.0   
mode           0    600.0
Name: trip_duration_seconds, dtype:...   
max                                                       5100.0   
min                                                        300.0   
std_dev                                               554.333278   
variance                                           307285.382701   
skewness                                                2.983264   
kurtosis                                                13.88312   
percentile_25                                              600.0   
percentile_75                                              900.0   
iqr                                                        300.0   
range                                                     4800.0   
cv                                                      0.658186   
qd                                                           0.2   
cs                                                      0.005382   
ck                                                      0.025045   
cvs                                                     0.005382   
cvk                                                     0.025045   
cvcs                                                    0.005382   
cvck                                                    0.025045   
cvcv                                                    0.658186   
cvqd                                                         0.2   
cvr                                                      5.69927   
cvm                                                          1.0   
cvmed                                                   0.712409   
cvmode         0    0.712409
Name: trip_duration_seconds, dty...   

column                                  trip_distance_kilometers  
rows                                                         732  
sum                                                  1235.013242  
mean                                                    1.687177  
median                                                  1.301309  
mode           0      0.100174
1      0.101307
2      0.10462...  
max                                                     9.215283  
min                                                     0.100174  
std_dev                                                 1.412409  
variance                                                1.994899  
skewness                                                1.747395  
kurtosis                                                4.141988  
percentile_25                                           0.665587  
percentile_75                                            2.17173  
iqr                                                     1.506143  
range                                                   9.115109  
cv                                                      0.837144  
qd                                                      0.530833  
cs                                                      1.237174  
ck                                                       2.93257  
cvs                                                     1.237174  
cvk                                                      2.93257  
cvcs                                                    1.237174  
cvck                                                     2.93257  
cvcv                                                    0.837144  
cvqd                                                    0.530833  
cvr                                                     5.402582  
cvm                                                          1.0  
cvmed                                                   0.771294  
cvmode         0

In [96]:
# get entries where trips start and end at station
midday_no_delay_tier_station_station = midday_no_delay_tier[midday_no_delay_tier['end_stop_id'].notna() & midday_no_delay_tier['start_stop_id'].notna()]
midday_no_delay_tier_station_station

tier_trips_id tier_trips_start_time tier_trips_end_time vehicle type  \
3218453      782399383   2023-07-01 10:10:00 2023-07-01 10:30:00    e-scooter   
3162300      782348970   2023-07-01 10:50:00 2023-07-01 10:55:00    e-scooter   
3070408      782316392   2023-07-01 10:50:00 2023-07-01 11:00:00    e-scooter   
3138620      782338840   2023-07-01 11:10:00 2023-07-01 11:25:00    e-scooter   
3067118      782314862   2023-07-01 11:15:00 2023-07-01 11:20:00    e-scooter   
...                ...                   ...                 ...          ...   
3487832      832267951   2023-07-31 11:05:00 2023-07-31 11:20:00    e-scooter   
3511770      832290915   2023-07-31 11:05:00 2023-07-31 11:15:00    e-scooter   
3373057      832157820   2023-07-31 11:25:00 2023-07-31 11:35:00    e-scooter   
3413162      832196289   2023-07-31 11:55:00 2023-07-31 12:10:00    e-scooter   
3320476      832121449   2023-07-31 11:55:00 2023-07-31 12:10:00    e-scooter   

          trip_duration  trip_distance_kilometers  trip_distance_meters  \
3218453 0 days 00:20:00                  2.085635           2085.634762   
3162300 0 days 00:05:00                  0.421335            421.334634   
3070408 0 days 00:10:00                  0.321411            321.411342   
3138620 0 days 00:15:00                  1.446943           1446.942565   
3067118 0 days 00:05:00                  0.792433            792.432886   
...                 ...                       ...                   ...   
3487832 0 days 00:15:00                  2.498630           2498.629525   
3511770 0 days 00:10:00                  0.857692            857.692480   
3373057 0 days 00:10:00                  0.852439            852.439337   
3413162 0 days 00:15:00                  0.987710            987.710077   
3320476 0 days 00:15:00                  2.855111           2855.111425   

         start_stop_id                            start_stop_name  \
3218453          687.0                                   Bonn Hbf   
3162300          688.0                                  Bonn West   
3070408         1102.0                         Bonn Friedensplatz   
3138620          694.0                     Bonn Tannenbusch Mitte   
3067118         2304.0                        Bonn Alte Schulstr.   
...                ...                                        ...   
3487832         1115.0  Bonn Bertha-Von-Suttner-Pl./Beethovenhaus   
3511770         1110.0                         Bonn Wilhelmsplatz   
3373057         1140.0                            Bonn Mozartstr.   
3413162          687.0                                   Bonn Hbf   
3320476           43.0                        Bonn Propsthof Nord   

                                         start_buffer_zone  end_stop_id  \
3218453  801621     POLYGON ((7.157885983913106 50.7227...       1181.0   
3162300  801621     POLYGON ((7.157885983913106 50.7227...       1194.0   
3070408  801621     POLYGON ((7.157885983913106 50.7227...       1115.0   
3138620  801621     POLYGON ((7.157885983913106 50.7227...        697.0   
3067118  801621     POLYGON ((7.157885983913106 50.7227...       1521.0   
...                                                    ...          ...   
3487832  801621     POLYGON ((7.157885983913106 50.7227...       1192.0   
3511770  801621     POLYGON ((7.157885983913106 50.7227...        687.0   
3373057  801621     POLYGON ((7.157885983913106 50.7227...        687.0   
3413162  801621     POLYGON ((7.157885983913106 50.7227...       1140.0   
3320476  801621     POLYGON ((7.157885983913106 50.7227...        697.0   

                                     end_stop_name  \
3218453                           Bonn Am Nordpark   
3162300                  Bonn Eifelstr./Macke-Haus   
3070408  Bonn Bertha-Von-Suttner-Pl./Beethovenhaus   
3138620                             Bonn Dransdorf   
3067118                        Bonn Vilich-Müldorf   
...                                            ...   
3487832                    

In [97]:
midday_no_delay_tier_station_station.describe()

tier_trips_id          tier_trips_start_time  \
count   3.470000e+02                            347   
mean    7.970316e+08  2023-07-15 08:35:05.187320064   
min     7.822657e+08            2023-07-01 10:10:00   
25%     7.823803e+08            2023-07-08 10:17:30   
50%     7.824597e+08            2023-07-13 11:40:00   
75%     8.087347e+08            2023-07-22 11:25:00   
max     8.323066e+08            2023-07-31 11:55:00   
std     1.622755e+07                            NaN   

                 tier_trips_end_time              trip_duration  \
count                            347                        347   
mean   2023-07-15 08:47:29.567723264  0 days 00:12:24.380403458   
min              2023-07-01 10:30:00            0 days 00:05:00   
25%              2023-07-08 10:27:30            0 days 00:10:00   
50%              2023-07-13 11:50:00            0 days 00:10:00   
75%              2023-07-22 11:40:00            0 days 00:15:00   
max              2023-07-31 12:10:00            0 days 00:55:00   
std                              NaN  0 days 00:06:59.525405497   

       trip_distance_kilometers  trip_distance_meters  start_stop_id  \
count                347.000000            347.000000     347.000000   
mean                   1.282640           1282.639906    1270.357349   
min                    0.100174            100.173813      43.000000   
25%                    0.538799            538.798901     687.000000   
50%                    0.965572            965.571703    1115.000000   
75%                    1.784008           1784.007854    1243.000000   
max                    5.802843           5802.843103    9702.000000   
std                    1.066740           1066.739712    1292.610778   

       end_stop_id  trip_duration_seconds  
count   347.000000             347.000000  
mean   1488.734870             744.380403  
min      43.000000             300.000000  
25%    1106.000000             600.000000  
50%    1161.000000             600.000000  
75%    1240.000000             900.000000  
max    9780.000000            3300.000000  
std    1605.190275             419.525405

In [98]:
# get statistics for the tier trips that start and end at a station
get_stats(midday_no_delay_tier_station_station, ['trip_duration_seconds', 'trip_distance_kilometers'])

column                                     trip_duration_seconds  \
rows                                                         347   
sum                                                     258300.0   
mean                                                  744.380403   
median                                                     600.0   
mode           0    600.0
Name: trip_duration_seconds, dtype:...   
max                                                       3300.0   
min                                                        300.0   
std_dev                                               419.525405   
variance                                           176001.565858   
skewness                                                2.184841   
kurtosis                                                8.337027   
percentile_25                                              600.0   
percentile_75                                              900.0   
iqr                                                        300.0   
range                                                     3000.0   
cv                                                       0.56359   
qd                                                           0.2   
cs                                                      0.005208   
ck                                                      0.019873   
cvs                                                     0.005208   
cvk                                                     0.019873   
cvcs                                                    0.005208   
cvck                                                    0.019873   
cvcv                                                     0.56359   
cvqd                                                         0.2   
cvr                                                     4.030197   
cvm                                                          1.0   
cvmed                                                   0.806039   
cvmode         0    0.806039
Name: trip_duration_seconds, dty...   

column                                  trip_distance_kilometers  
rows                                                         347  
sum                                                   445.076047  
mean                                                     1.28264  
median                                                  0.965572  
mode           0      0.100174
1      0.104626
2      0.10762...  
max                                                     5.802843  
min                                                     0.100174  
std_dev                                                  1.06674  
variance                                                1.137934  
skewness                                                1.615134  
kurtosis                                                3.072687  
percentile_25                                           0.538799  
percentile_75                                           1.784008  
iqr                                                     1.245209  
range                                                   5.702669  
cv                                                      0.831675  
qd                                                      0.536079  
cs                                                      1.514085  
ck                                                      2.880447  
cvs                                                     1.514085  
cvk                                                     2.880447  
cvcs                                                    1.514085  
cvck                                                    2.880447  
cvcv                                                    0.831675  
cvqd                                                    0.536079  
cvr                                                     4.446041  
cvm                                                          1.0  
cvmed                                                     0.7528  
cvmode         0

In [99]:
midday_no_delay_next = check_micromobility_datasets('next', midday_no_delay)

In [100]:
midday_no_delay_next.describe()

nextbike_trips_id      nextbike_trips_start_time  \
count       2.059000e+03                           2059   
mean        3.794365e+07  2023-07-15 11:50:07.255949312   
min         3.771653e+07            2023-07-01 10:01:00   
25%         3.782706e+07            2023-07-07 11:56:00   
50%         3.794664e+07            2023-07-14 10:51:00   
75%         3.805304e+07            2023-07-22 23:06:00   
max         3.817123e+07            2023-07-31 12:01:00   
std         1.308456e+05                            NaN   

             nextbike_trips_end_time              trip_duration  \
count                           2059                       2059   
mean   2023-07-15 12:04:07.226809344  0 days 00:13:59.970859640   
min              2023-07-01 10:11:00            0 days 00:05:00   
25%              2023-07-07 12:11:00            0 days 00:10:00   
50%              2023-07-14 11:06:00            0 days 00:10:00   
75%              2023-07-22 23:43:30            0 days 00:15:00   
max              2023-07-31 12:31:00            0 days 01:55:00   
std                              NaN  0 days 00:09:03.456703569   

       trip_distance_kilometers  trip_distance_meters  start_stop_id  \
count               2059.000000           2059.000000    1749.000000   
mean                   1.575282           1575.282070    1060.121784   
min                    0.100624            100.624321      43.000000   
25%                    0.734590            734.589517     687.000000   
50%                    1.250257           1250.257368    1115.000000   
75%                    1.939845           1939.844841    1221.000000   
max                    9.474703           9474.703414    9780.000000   
std                    1.326055           1326.055013     721.095317   

       end_stop_id  trip_duration_seconds  
count  1245.000000            2059.000000  
mean   1196.127711             839.970860  
min      43.000000             300.000000  
25%     689.000000             600.000000  
50%    1140.000000             600.000000  
75%    1221.000000             900.000000  
max    9780.000000            6900.000000  
std    1105.235098             543.456704

In [101]:
get_stats(midday_no_delay_next, ['trip_duration_seconds', 'trip_distance_kilometers'])

column                                     trip_duration_seconds  \
rows                                                        2059   
sum                                                    1729500.0   
mean                                                   839.97086   
median                                                     600.0   
mode           0    600.0
Name: trip_duration_seconds, dtype:...   
max                                                       6900.0   
min                                                        300.0   
std_dev                                               543.456704   
variance                                           295345.188655   
skewness                                                3.822066   
kurtosis                                               25.415869   
percentile_25                                              600.0   
percentile_75                                              900.0   
iqr                                                        300.0   
range                                                     6600.0   
cv                                                      0.646995   
qd                                                           0.2   
cs                                                      0.007033   
ck                                                      0.046767   
cvs                                                     0.007033   
cvk                                                     0.046767   
cvcs                                                    0.007033   
cvck                                                    0.046767   
cvcv                                                    0.646995   
cvqd                                                         0.2   
cvr                                                     7.857415   
cvm                                                          1.0   
cvmed                                                    0.71431   
cvmode         0    0.71431
Name: trip_duration_seconds, dtyp...   

column                                  trip_distance_kilometers  
rows                                                        2059  
sum                                                  3243.505783  
mean                                                    1.575282  
median                                                  1.250257  
mode           0    0.372996
1    1.087753
Name: trip_distanc...  
max                                                     9.474703  
min                                                     0.100624  
std_dev                                                 1.326055  
variance                                                1.758422  
skewness                                                2.257127  
kurtosis                                                6.795334  
percentile_25                                            0.73459  
percentile_75                                           1.939845  
iqr                                                     1.205255  
range                                                   9.374079  
cv                                                      0.841789  
qd                                                      0.450658  
cs                                                      1.702137  
ck                                                      5.124474  
cvs                                                     1.702137  
cvk                                                     5.124474  
cvcs                                                    1.702137  
cvck                                                    5.124474  
cvcv                                                    0.841789  
cvqd                                                    0.450658  
cvr                                                     5.950731  
cvm                                                          1.0  
cvmed                                                   0.793672  
cvmode         0

In [102]:
# get entries where trips start and end at station
midday_no_delay_next_station_station = midday_no_delay_next[midday_no_delay_next['end_stop_id'].notna() & midday_no_delay_next['start_stop_id'].notna()]
midday_no_delay_next_station_station

nextbike_trips_id nextbike_trips_start_time nextbike_trips_end_time  \
1438661           38010471       2023-07-01 10:11:00     2023-07-01 10:21:00   
1377777           37917339       2023-07-01 10:16:00     2023-07-01 10:26:00   
1516357           38070516       2023-07-01 10:21:00     2023-07-01 10:36:00   
1395352           37949936       2023-07-01 10:26:00     2023-07-01 10:36:00   
1393345           37985223       2023-07-01 10:36:00     2023-07-01 10:46:00   
...                    ...                       ...                     ...   
1569214           38116283       2023-07-31 11:51:00     2023-07-31 11:56:00   
1579531           37749462       2023-07-31 11:56:00     2023-07-31 12:06:00   
1280469           37868635       2023-07-31 11:56:00     2023-07-31 12:06:00   
1539398           38089356       2023-07-31 11:56:00     2023-07-31 12:16:00   
1589964           38131131       2023-07-31 12:01:00     2023-07-31 12:11:00   

         nextbike_trips_start_at_station  nextbike_trips_end_at_station  \
1438661                            False                          False   
1377777                            False                          False   
1516357                            False                          False   
1395352                            False                          False   
1393345                            False                          False   
...                                  ...                            ...   
1569214                            False                          False   
1579531                            False                           True   
1280469                            False                          False   
1539398                            False                          False   
1589964                            False                          False   

        vehicle type   trip_duration  trip_distance_kilometers  \
1438661         bike 0 days 00:10:00                  0.931129   
1377777         bike 0 days 00:10:00                  0.990373   
1516357         bike 0 days 00:15:00                  2.408581   
1395352         bike 0 days 00:10:00                  1.306276   
1393345         bike 0 days 00:10:00                  1.211956   
...              ...             ...                       ...   
1569214         bike 0 days 00:05:00                  0.499254   
1579531         bike 0 days 00:10:00                  0.294753   
1280469         bike 0 days 00:10:00                  0.626191   
1539398         bike 0 days 00:20:00                  1.740175   
1589964         bike 0 days 00:10:00                  1.778861   

         trip_distance_meters  \
1438661            931.128902   
1377777            990.372654   
1516357           2408.581219   
1395352           1306.275793   
1393345           1211.955564   
...                       ...   
1569214            499.253733   
1579531            294.753461   
1280469            626.191244   
1539398           1740.174844   
1589964           1778.860503   

                                            start_location  \
1438661  b'\x01\x01\x00\x00\x00!\xae\x9c\xbd3z\x1c@\xea...   
1377777  b'\x01\x01\x00\x00\x00\xa6H\xbe\x12HY\x1c@\x86...   
1516357  b'\x01\x01\x00\x00\x00X\x8f\xfbV\xebT\x1c@L\xc...   
1395352  b'\x01\x01\x00\x00\x00\x8d\xd0\xcf\xd4\xebf\x1...   
1393345  b'\x01\x01\x00\x00\x00\xc3\xbb\\\xc4wb\x1c@\xc...   
...                                                    ...   
1569214  b'\x01\x01\x00\x00\x00\xf7\x90\xf0\xbd\xbfa\x1...   
1579531  b'\x01\x01\x00\x00\x00-\xe9(\x07\xb3i\x1c@C\x9...   
1280469  b'\x01\x01\x00\x00\x00/\x15\x1b\xf3:b\x1c@b\xd...   
1539398  b'\x01\x01\x00\x00\x00\xe9\x0b!\xe7\xfd_\x1c@\...   
1589964  b'\x01\x01\x00\x00\x00\x157n1?W\x1c@"\x8euq\x1...   

                                              end_location  start_stop_id  \
1438661  b'\x01\x01\x00\x00\x00?n\xbf|\xb2\x82\x1c@\x92...         1500.0   
1377777  b'\x01\x01\x00\x00\x00\xd3Mb\x10XY\x1c@\xe1\xb...

In [103]:
midday_no_delay_next_station_station.describe()

nextbike_trips_id      nextbike_trips_start_time  \
count       1.132000e+03                           1132   
mean        3.794549e+07  2023-07-15 10:32:34.876325120   
min         3.771668e+07            2023-07-01 10:11:00   
25%         3.783647e+07            2023-07-08 10:01:00   
50%         3.794536e+07            2023-07-14 10:36:00   
75%         3.805033e+07            2023-07-22 11:11:00   
max         3.817123e+07            2023-07-31 12:01:00   
std         1.290809e+05                            NaN   

             nextbike_trips_end_time              trip_duration  \
count                           1132                       1132   
mean   2023-07-15 10:45:38.533568768  0 days 00:13:03.657243816   
min              2023-07-01 10:21:00            0 days 00:05:00   
25%              2023-07-08 10:11:00            0 days 00:10:00   
50%              2023-07-14 10:51:00            0 days 00:10:00   
75%              2023-07-22 11:27:15            0 days 00:15:00   
max              2023-07-31 12:31:00            0 days 01:55:00   
std                              NaN  0 days 00:08:00.115351423   

       trip_distance_kilometers  trip_distance_meters  start_stop_id  \
count               1132.000000           1132.000000    1132.000000   
mean                   1.362872           1362.871593    1100.189046   
min                    0.100624            100.624321      43.000000   
25%                    0.745714            745.714429     687.000000   
50%                    1.198652           1198.651822    1115.000000   
75%                    1.688760           1688.760210    1221.000000   
max                    8.017719           8017.718903    9478.000000   
std                    0.998887            998.886605     802.589360   

       end_stop_id  trip_duration_seconds  
count  1132.000000            1132.000000  
mean   1211.793286             783.657244  
min      43.000000             300.000000  
25%     693.000000             600.000000  
50%    1140.000000             600.000000  
75%    1221.000000             900.000000  
max    9780.000000            6900.000000  
std    1110.300567             480.115351

In [104]:
# get statistics for the tier trips that start and end at a station
get_stats(midday_no_delay_next_station_station, ['trip_duration_seconds', 'trip_distance_kilometers'])

column                                     trip_duration_seconds  \
rows                                                        1132   
sum                                                     887100.0   
mean                                                  783.657244   
median                                                     600.0   
mode           0    600.0
Name: trip_duration_seconds, dtype:...   
max                                                       6900.0   
min                                                        300.0   
std_dev                                               480.115351   
variance                                           230510.750673   
skewness                                                4.751186   
kurtosis                                               42.112221   
percentile_25                                              600.0   
percentile_75                                              900.0   
iqr                                                        300.0   
range                                                     6600.0   
cv                                                       0.61266   
qd                                                           0.2   
cs                                                      0.009896   
ck                                                      0.087713   
cvs                                                     0.009896   
cvk                                                     0.087713   
cvcs                                                    0.009896   
cvck                                                    0.087713   
cvcv                                                     0.61266   
cvqd                                                         0.2   
cvr                                                     8.422049   
cvm                                                          1.0   
cvmed                                                   0.765641   
cvmode         0    0.765641
Name: trip_duration_seconds, dty...   

column                                  trip_distance_kilometers  
rows                                                        1132  
sum                                                  1542.770644  
mean                                                    1.362872  
median                                                  1.198652  
mode           0    1.087753
Name: trip_distance_kilometers, ...  
max                                                     8.017719  
min                                                     0.100624  
std_dev                                                 0.998887  
variance                                                0.997774  
skewness                                                2.357412  
kurtosis                                                8.964593  
percentile_25                                           0.745714  
percentile_75                                            1.68876  
iqr                                                     0.943046  
range                                                   7.917095  
cv                                                      0.732928  
qd                                                      0.387371  
cs                                                      2.360039  
ck                                                      8.974585  
cvs                                                     2.360039  
cvk                                                     8.974585  
cvcs                                                    2.360039  
cvck                                                    8.974585  
cvcv                                                    0.732928  
cvqd                                                    0.387371  
cvr                                                     5.809127  
cvm                                                          1.0  
cvmed                                                   0.879505  
cvmode         0

In [105]:
midday_nan_delay = nan_delay[(nan_delay['scheduled_arrival_time'].dt.hour > 9) & (nan_delay['scheduled_arrival_time'].dt.hour < 12)]
midday_nan_delay

route_id  agency_id route_short_name  route_type route_type_name  \
16911         537          8              537           3             Bus   
16912         610          6              610           3             Bus   
16914          66          6               66           0            Tram   
16919         632          6              632           3             Bus   
16920         606          6              606           3             Bus   
...           ...        ...              ...         ...             ...   
2505830       604          6              604           3             Bus   
2505832       633          6              633           3             Bus   
2505833       614          6              614           3             Bus   
2505836       605          6              605           3             Bus   
2505837       602          6              602           3             Bus   

                                      agency_name  service_id  \
16911    RSVG Rhein-Sieg-Verkehrsgesellschaft mbH         130   
16912           SWB Stadtwerke Bonn Verkehrs GmbH         130   
16914           SWB Stadtwerke Bonn Verkehrs GmbH       26814   
16919           SWB Stadtwerke Bonn Verkehrs GmbH         130   
16920           SWB Stadtwerke Bonn Verkehrs GmbH         130   
...                                           ...         ...   
2505830         SWB Stadtwerke Bonn Verkehrs GmbH          64   
2505832         SWB Stadtwerke Bonn Verkehrs GmbH          64   
2505833         SWB Stadtwerke Bonn Verkehrs GmbH          64   
2505836         SWB Stadtwerke Bonn Verkehrs GmbH          64   
2505837         SWB Stadtwerke Bonn Verkehrs GmbH          64   

                                                   trip_id  \
16911    129-537-008-687.2.36:093900-37-1_F8383784-39A7...   
16912    6100144-610-006-1341.2.24:095300-53-1_35A26FA1...   
16914    660163-66-006-1788.1.11:093200-24-178_DA129678...   
16919    6320194-632-006-8832.2.23:095400-26-1_DCDB4744...   
16920    6060152-606-006-1584.2.22:095400-44-1_4B496488...   
...                                                    ...   
2505830  6040058-604-006-678.2.21:114300-51-1_FF99F574-...   
2505832  6330034-633-006-1584.2.24:114300-24-1_89BA5E45...   
2505833  6140038-614-006-1607.2.22:115400-19-1_D8273181...   
2505836  6050080-605-006-1415.2.22:112300-43-1_B4079C7C...   
2505837  6020062-602-006-9478.2.22:111800-39-1_DBAEC13E...   

              trip_headsign  direction_id  ...  delay_span  \
16911       Oberpleis Busbf             1  ...           0   
16912          Giselherstr.             1  ...           0   
16914             Stadthaus             0  ...           0   
16919       Uniklinikum Süd             1  ...           0   
16920    Hardtberg Klinikum             1  ...           0   
...                     ...           ...  ...         ...   
2505830     Ückesdorf Mitte             1  ...           0   
2505832    Endenich Nord Bf             1  ...           0   
2505833        Im Rosenberg             1  ...           0   
2505836         Duisdorf Bf             1  ...           0   
2505837              Waldau             1  ...           0   

         arrival_delay_span weather_int time_span_arrival  \
16911                     0           1                 0   
16912                     0           1                 0   
16914                     0           1                 0   
16919                     0           1                 0   
16920                     0           1                 0   
...                     ...         ...               ...   
2505830                   0           0                 0   
2505832                   0           0                 0   
2505833                   0           0                 0   
2505836                   0           0                 0   
2505837                   0           0                 0   

         time_span_int_arrival  weekend time_span time_span_int  \
16911        

In [106]:
get_stats(midday_nan_delay, ['tier_trips_count', 'tier_trips_end_at_station_count', 'nextbike_trips_count', 'nextbike_trips_end_at_station_count', 'current_temp', 'current_precipitation_volume'])

/tmp/ipykernel_2575952/41814695.py:51: RuntimeWarning: invalid value encountered in scalar divide
  qd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:55: RuntimeWarning: invalid value encountered in scalar divide
  cvqd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:51: RuntimeWarning: invalid value encountered in scalar divide
  qd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:55: RuntimeWarning: invalid value encountered in scalar divide
  cvqd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:51: RuntimeWarning: invalid value encountered in scalar divide
  qd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:55: RuntimeWarning: invalid value encountered in scalar divide
  cvqd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:51: RuntimeWarning: invalid value encountered in scalar divide
  qd = iqr / (percentile_75 + percenti

column                                        tier_trips_count  \
rows                                                    127015   
sum                                                       2270   
mean                                                  0.017872   
median                                                     0.0   
mode               0    0
Name: tier_trips_count, dtype: int64   
max                                                          5   
min                                                          0   
std_dev                                               0.145838   
variance                                              0.021269   
skewness                                              9.778614   
kurtosis                                            126.729609   
percentile_25                                              0.0   
percentile_75                                              0.0   
iqr                                                        0.0   
range                                                        5   
cv                                                     8.16019   
qd                                                         NaN   
cs                                                   67.051139   
ck                                                  868.974373   
cvs                                                  67.051139   
cvk                                                 868.974373   
cvcs                                                 67.051139   
cvck                                                868.974373   
cvcv                                                   8.16019   
cvqd                                                       NaN   
cvr                                                 279.768722   
cvm                                                        1.0   
cvmed                                                      0.0   
cvmode         0    0.0
Name: tier_trips_count, dtype: float64   

column                           tier_trips_end_at_station_count  \
rows                                                      127015   
sum                                                         1879   
mean                                                    0.014794   
median                                                       0.0   
mode           0    0
Name: tier_trips_end_at_station_count, ...   
max                                                            5   
min                                                            0   
std_dev                                                 0.132063   
variance                                                0.017441   
skewness                                               10.618239   
kurtosis                                              149.313272   
percentile_25                                                0.0   
percentile_75                                                0.0   
iqr                                                          0.0   
range                                                          5   
cv                                                      8.927075   
qd                                                           NaN   
cs                                                     80.402867   
ck                                                   1130.622038   
cvs                                                    80.402867   
cvk                                                  1130.622038   
cvcs                                                   80.402867   
cvck                                                 1130.622038   
cvcv                                                    8.927075   
cvqd                                                         NaN   
cvr                                                   337.985631   
cvm                                                          1.0   
cvmed                                                        0.0   
cvmode         0    0.0
Name: tier_trips_end_at

In [107]:
midday_nan_delay_tier = check_micromobility_datasets('tier', midday_nan_delay)

In [108]:
midday_nan_delay_tier.describe()

tier_trips_id       tier_trips_start_time  \
count   1.125000e+03                        1125   
mean    7.973398e+08  2023-07-15 07:54:18.400000   
min     7.822648e+08         2023-07-01 10:00:00   
25%     7.823699e+08         2023-07-07 11:35:00   
50%     8.086221e+08         2023-07-14 10:20:00   
75%     8.087299e+08         2023-07-22 10:45:00   
max     8.323066e+08         2023-07-31 11:55:00   
std     1.593333e+07                         NaN   

                 tier_trips_end_time              trip_duration  \
count                           1125                       1125   
mean   2023-07-15 08:08:00.266666752  0 days 00:13:41.866666666   
min              2023-07-01 10:10:00            0 days 00:05:00   
25%              2023-07-07 11:50:00            0 days 00:10:00   
50%              2023-07-14 10:25:00            0 days 00:10:00   
75%              2023-07-22 10:55:00            0 days 00:15:00   
max              2023-07-31 12:40:00            0 days 01:40:00   
std                              NaN  0 days 00:09:48.594199489   

       trip_distance_kilometers  trip_distance_meters  start_stop_id  \
count               1125.000000           1125.000000     845.000000   
mean                   1.660816           1660.815675    1519.403550   
min                    0.100174            100.173813      43.000000   
25%                    0.631261            631.261258     699.000000   
50%                    1.239928           1239.928178    1115.000000   
75%                    2.178571           2178.570977    1431.000000   
max                   13.908704          13908.703513    9703.000000   
std                    1.490705           1490.704522    1737.064463   

       end_stop_id  trip_duration_seconds  
count   624.000000            1125.000000  
mean   1438.884615             821.866667  
min      43.000000             300.000000  
25%    1103.000000             600.000000  
50%    1150.500000             600.000000  
75%    1241.500000             900.000000  
max    9780.000000            6000.000000  
std    1561.960700             588.594199

In [109]:
get_stats(midday_nan_delay_tier, ['trip_duration_seconds', 'trip_distance_kilometers'])

column                                     trip_duration_seconds  \
rows                                                        1125   
sum                                                     924600.0   
mean                                                  821.866667   
median                                                     600.0   
mode           0    600.0
Name: trip_duration_seconds, dtype:...   
max                                                       6000.0   
min                                                        300.0   
std_dev                                               588.594199   
variance                                           346443.131673   
skewness                                                 3.55301   
kurtosis                                               19.824896   
percentile_25                                              600.0   
percentile_75                                              900.0   
iqr                                                        300.0   
range                                                     5700.0   
cv                                                      0.716168   
qd                                                           0.2   
cs                                                      0.006036   
ck                                                      0.033682   
cvs                                                     0.006036   
cvk                                                     0.033682   
cvcs                                                    0.006036   
cvck                                                    0.033682   
cvcv                                                    0.716168   
cvqd                                                         0.2   
cvr                                                     6.935432   
cvm                                                          1.0   
cvmed                                                   0.730045   
cvmode         0    0.730045
Name: trip_duration_seconds, dty...   

column                                  trip_distance_kilometers  
rows                                                        1125  
sum                                                  1868.417634  
mean                                                    1.660816  
median                                                  1.239928  
mode           0        0.100174
1        0.104626
2        0...  
max                                                    13.908704  
min                                                     0.100174  
std_dev                                                 1.490705  
variance                                                  2.2222  
skewness                                                2.199555  
kurtosis                                                7.981332  
percentile_25                                           0.631261  
percentile_75                                           2.178571  
iqr                                                      1.54731  
range                                                   13.80853  
cv                                                      0.897574  
qd                                                      0.550677  
cs                                                      1.475514  
ck                                                      5.354067  
cvs                                                     1.475514  
cvk                                                     5.354067  
cvcs                                                    1.475514  
cvck                                                    5.354067  
cvcv                                                    0.897574  
cvqd                                                    0.550677  
cvr                                                     8.314306  
cvm                                                          1.0  
cvmed                                                   0.746578  
cvmode         0

In [110]:
# get entries where trips start and end at station
midday_nan_delay_tier_station_station = midday_nan_delay_tier[midday_nan_delay_tier['end_stop_id'].notna() & midday_nan_delay_tier['start_stop_id'].notna()]
midday_nan_delay_tier_station_station

tier_trips_id tier_trips_start_time tier_trips_end_time vehicle type  \
3254798      782432527   2023-07-01 10:00:00 2023-07-01 10:10:00    e-scooter   
3218453      782399383   2023-07-01 10:10:00 2023-07-01 10:30:00    e-scooter   
3276752      782452510   2023-07-01 10:10:00 2023-07-01 10:20:00    e-scooter   
3276328      782452113   2023-07-01 10:10:00 2023-07-01 10:30:00    e-scooter   
2946124      782277489   2023-07-01 10:35:00 2023-07-01 10:45:00    e-scooter   
...                ...                   ...                 ...          ...   
3373057      832157820   2023-07-31 11:25:00 2023-07-31 11:35:00    e-scooter   
3349076      832140951   2023-07-31 11:30:00 2023-07-31 11:35:00    e-scooter   
3426831      832209369   2023-07-31 11:40:00 2023-07-31 11:55:00    e-scooter   
3329228      832127396   2023-07-31 11:50:00 2023-07-31 12:00:00    e-scooter   
3413162      832196289   2023-07-31 11:55:00 2023-07-31 12:10:00    e-scooter   

          trip_duration  trip_distance_kilometers  trip_distance_meters  \
3254798 0 days 00:10:00                  1.514264           1514.264285   
3218453 0 days 00:20:00                  2.085635           2085.634762   
3276752 0 days 00:10:00                  0.662632            662.632417   
3276328 0 days 00:20:00                  2.824580           2824.579934   
2946124 0 days 00:10:00                  0.733965            733.964543   
...                 ...                       ...                   ...   
3373057 0 days 00:10:00                  0.852439            852.439337   
3349076 0 days 00:05:00                  0.315999            315.999193   
3426831 0 days 00:15:00                  2.443477           2443.477315   
3329228 0 days 00:10:00                  0.661794            661.794368   
3413162 0 days 00:15:00                  0.987710            987.710077   

         start_stop_id                            start_stop_name  \
3254798         1103.0                                 Bonn Markt   
3218453          687.0                                   Bonn Hbf   
3276752          686.0                     Bonn Universität/Markt   
3276328         1234.0                      Bonn Am Klostergarten   
2946124         1958.0                      Bonn An Der Wolfsburg   
...                ...                                        ...   
3373057         1140.0                            Bonn Mozartstr.   
3349076         1115.0  Bonn Bertha-Von-Suttner-Pl./Beethovenhaus   
3426831         9702.0                        Bonn Im Tannenbusch   
3329228         1111.0                Bonn Beethovenhalle Und Swb   
3413162          687.0                                   Bonn Hbf   

                                         start_buffer_zone  end_stop_id  \
3254798  801621     POLYGON ((7.157885983913106 50.7227...       1133.0   
3218453  801621     POLYGON ((7.157885983913106 50.7227...       1181.0   
3276752  801621     POLYGON ((7.157885983913106 50.7227...       2667.0   
3276328  801621     POLYGON ((7.157885983913106 50.7227...        687.0   
2946124  801621     POLYGON ((7.157885983913106 50.7227...       1500.0   
...                                                    ...          ...   
3373057  801621     POLYGON ((7.157885983913106 50.7227...        687.0   
3349076  801621     POLYGON ((7.157885983913106 50.7227...       1102.0   
3426831  801621     POLYGON ((7.157885983913106 50.7227...       1151.0   
3329228  801621     POLYGON ((7.157885983913106 50.7227...       1102.0   
3413162  801621     POLYGON ((7.157885983913106 50.7227...       1140.0   

                                     end_stop_name  \
3254798                            Bonn Luisenstr.   
3218453                           Bonn Am Nordpark   
3276752  Bonn Brüdergasse/Bertha-Von-Suttner-Platz   
3276328                                   Bonn Hbf   
2946124                 Bonn Konrad-Adenauer-Platz   
...                                            ...   
3373057                    

In [111]:
midday_nan_delay_tier_station_station.describe()

tier_trips_id          tier_trips_start_time  \
count   5.310000e+02                            531   
mean    7.969939e+08  2023-07-15 09:03:29.039547904   
min     7.822648e+08            2023-07-01 10:00:00   
25%     7.823810e+08            2023-07-08 10:50:00   
50%     8.086222e+08            2023-07-14 10:25:00   
75%     8.087216e+08            2023-07-21 11:50:00   
max     8.323066e+08            2023-07-31 11:55:00   
std     1.542764e+07                            NaN   

                 tier_trips_end_time              trip_duration  \
count                            531                        531   
mean   2023-07-15 09:15:55.932203264  0 days 00:12:26.892655367   
min              2023-07-01 10:10:00            0 days 00:05:00   
25%              2023-07-08 11:00:00            0 days 00:10:00   
50%              2023-07-14 10:35:00            0 days 00:10:00   
75%              2023-07-21 11:55:00            0 days 00:15:00   
max              2023-07-31 12:10:00            0 days 00:55:00   
std                              NaN  0 days 00:07:13.899329427   

       trip_distance_kilometers  trip_distance_meters  start_stop_id  \
count                531.000000            531.000000     531.000000   
mean                   1.380911           1380.910593    1581.220339   
min                    0.100174            100.173813      43.000000   
25%                    0.558675            558.675267    1102.000000   
50%                    1.088021           1088.021395    1115.000000   
75%                    1.908243           1908.243201    1290.000000   
max                    6.401385           6401.384966    9703.000000   
std                    1.120084           1120.083913    1840.187411   

       end_stop_id  trip_duration_seconds  
count   531.000000             531.000000  
mean   1428.463277             746.892655  
min      43.000000             300.000000  
25%    1106.000000             600.000000  
50%    1153.000000             600.000000  
75%    1241.000000             900.000000  
max    9780.000000            3300.000000  
std    1469.196714             433.899329

In [112]:
# get statistics for the tier trips that start and end at a station
get_stats(midday_nan_delay_tier_station_station, ['trip_duration_seconds', 'trip_distance_kilometers'])

column                                     trip_duration_seconds  \
rows                                                         531   
sum                                                     396600.0   
mean                                                  746.892655   
median                                                     600.0   
mode           0    600.0
Name: trip_duration_seconds, dtype:...   
max                                                       3300.0   
min                                                        300.0   
std_dev                                               433.899329   
variance                                           188268.628078   
skewness                                                2.232915   
kurtosis                                                8.277624   
percentile_25                                              600.0   
percentile_75                                              900.0   
iqr                                                        300.0   
range                                                     3000.0   
cv                                                      0.580939   
qd                                                           0.2   
cs                                                      0.005146   
ck                                                      0.019077   
cvs                                                     0.005146   
cvk                                                     0.019077   
cvcs                                                    0.005146   
cvck                                                    0.019077   
cvcv                                                    0.580939   
cvqd                                                         0.2   
cvr                                                     4.016641   
cvm                                                          1.0   
cvmed                                                   0.803328   
cvmode         0    0.803328
Name: trip_duration_seconds, dty...   

column                                  trip_distance_kilometers  
rows                                                         531  
sum                                                   733.263525  
mean                                                    1.380911  
median                                                  1.088021  
mode           0      0.100174
1      0.104626
2      0.10540...  
max                                                     6.401385  
min                                                     0.100174  
std_dev                                                 1.120084  
variance                                                1.254588  
skewness                                                1.454528  
kurtosis                                                2.407257  
percentile_25                                           0.558675  
percentile_75                                           1.908243  
iqr                                                     1.349568  
range                                                   6.301211  
cv                                                       0.81112  
qd                                                      0.547066  
cs                                                      1.298589  
ck                                                      2.149175  
cvs                                                     1.298589  
cvk                                                     2.149175  
cvcs                                                    1.298589  
cvck                                                    2.149175  
cvcv                                                     0.81112  
cvqd                                                    0.547066  
cvr                                                     4.563084  
cvm                                                          1.0  
cvmed                                                   0.787901  
cvmode         0

In [113]:
midday_nan_delay_next = check_micromobility_datasets('next', midday_nan_delay)

In [114]:
midday_nan_delay_next.describe()

nextbike_trips_id      nextbike_trips_start_time  \
count       3.252000e+03                           3252   
mean        3.794066e+07  2023-07-15 08:35:45.055350784   
min         3.771653e+07            2023-07-01 10:01:00   
25%         3.782965e+07            2023-07-07 11:11:00   
50%         3.794219e+07            2023-07-14 10:31:00   
75%         3.804921e+07            2023-07-22 11:41:00   
max         3.817126e+07            2023-07-31 12:01:00   
std         1.284654e+05                            NaN   

             nextbike_trips_end_time              trip_duration  \
count                           3252                       3252   
mean   2023-07-15 08:49:56.808118016  0 days 00:14:11.752767527   
min              2023-07-01 10:11:00            0 days 00:05:00   
25%              2023-07-07 11:26:00            0 days 00:10:00   
50%              2023-07-14 10:46:00            0 days 00:10:00   
75%              2023-07-22 11:57:15            0 days 00:15:00   
max              2023-07-31 12:31:00            0 days 02:00:00   
std                              NaN  0 days 00:09:50.767689018   

       trip_distance_kilometers  trip_distance_meters  start_stop_id  \
count               3252.000000           3252.000000    2643.000000   
mean                   1.609110           1609.110439    1174.769958   
min                    0.100624            100.624321      43.000000   
25%                    0.704310            704.310490     687.000000   
50%                    1.238101           1238.100915    1115.000000   
75%                    2.029745           2029.744950    1221.000000   
max                   14.013714          14013.713672    9780.000000   
std                    1.429661           1429.661219    1071.873817   

       end_stop_id  trip_duration_seconds  
count  1979.000000            3252.000000  
mean   1207.091966             851.752768  
min      43.000000             300.000000  
25%     687.000000             600.000000  
50%    1135.000000             600.000000  
75%    1221.000000             900.000000  
max    9780.000000            7200.000000  
std    1144.840329             590.767689

In [115]:
get_stats(midday_nan_delay_next, ['trip_duration_seconds', 'trip_distance_kilometers'])

column                                     trip_duration_seconds  \
rows                                                        3252   
sum                                                    2769900.0   
mean                                                  851.752768   
median                                                     600.0   
mode           0    600.0
Name: trip_duration_seconds, dtype:...   
max                                                       7200.0   
min                                                        300.0   
std_dev                                               590.767689   
variance                                           349006.462389   
skewness                                                4.426465   
kurtosis                                               31.979226   
percentile_25                                              600.0   
percentile_75                                              900.0   
iqr                                                        300.0   
range                                                     6900.0   
cv                                                      0.693591   
qd                                                           0.2   
cs                                                      0.007493   
ck                                                      0.054132   
cvs                                                     0.007493   
cvk                                                     0.054132   
cvcs                                                    0.007493   
cvck                                                    0.054132   
cvcv                                                    0.693591   
cvqd                                                         0.2   
cvr                                                     8.100942   
cvm                                                          1.0   
cvmed                                                    0.70443   
cvmode         0    0.70443
Name: trip_duration_seconds, dtyp...   

column                                  trip_distance_kilometers  
rows                                                        3252  
sum                                                  5232.827148  
mean                                                     1.60911  
median                                                  1.238101  
mode           0    0.834842
1    0.870199
Name: trip_distanc...  
max                                                    14.013714  
min                                                     0.100624  
std_dev                                                 1.429661  
variance                                                2.043931  
skewness                                                2.586775  
kurtosis                                               10.387552  
percentile_25                                            0.70431  
percentile_75                                           2.029745  
iqr                                                     1.325434  
range                                                  13.913089  
cv                                                      0.888479  
qd                                                      0.484787  
cs                                                      1.809362  
ck                                                      7.265743  
cvs                                                     1.809362  
cvk                                                     7.265743  
cvcs                                                    1.809362  
cvck                                                    7.265743  
cvcv                                                    0.888479  
cvqd                                                    0.484787  
cvr                                                     8.646448  
cvm                                                          1.0  
cvmed                                                   0.769432  
cvmode         0

In [116]:
# get entries where trips start and end at station
midday_nan_delay_next_station_station = midday_nan_delay_next[midday_nan_delay_next['end_stop_id'].notna() & midday_nan_delay_next['start_stop_id'].notna()]
midday_nan_delay_next_station_station

nextbike_trips_id nextbike_trips_start_time nextbike_trips_end_time  \
1438661           38010471       2023-07-01 10:11:00     2023-07-01 10:21:00   
1433893           38006737       2023-07-01 10:21:00     2023-07-01 10:36:00   
1646587           37778006       2023-07-01 10:21:00     2023-07-01 10:31:00   
1516357           38070516       2023-07-01 10:21:00     2023-07-01 10:36:00   
1385300           37921324       2023-07-01 10:26:00     2023-07-01 10:41:00   
...                    ...                       ...                     ...   
1280469           37868635       2023-07-31 11:56:00     2023-07-31 12:06:00   
1539398           38089356       2023-07-31 11:56:00     2023-07-31 12:16:00   
1453284           38021980       2023-07-31 11:56:00     2023-07-31 12:01:00   
1306882           37881128       2023-07-31 12:01:00     2023-07-31 12:11:00   
1358515           37908633       2023-07-31 12:01:00     2023-07-31 12:16:00   

         nextbike_trips_start_at_station  nextbike_trips_end_at_station  \
1438661                            False                          False   
1433893                            False                          False   
1646587                            False                          False   
1516357                            False                          False   
1385300                            False                          False   
...                                  ...                            ...   
1280469                            False                          False   
1539398                            False                          False   
1453284                            False                          False   
1306882                            False                          False   
1358515                            False                          False   

        vehicle type   trip_duration  trip_distance_kilometers  \
1438661         bike 0 days 00:10:00                  0.931129   
1433893         bike 0 days 00:15:00                  3.604011   
1646587         bike 0 days 00:10:00                  1.381387   
1516357         bike 0 days 00:15:00                  2.408581   
1385300         bike 0 days 00:15:00                  1.362846   
...              ...             ...                       ...   
1280469         bike 0 days 00:10:00                  0.626191   
1539398         bike 0 days 00:20:00                  1.740175   
1453284         bike 0 days 00:05:00                  0.535144   
1306882         bike 0 days 00:10:00                  0.412296   
1358515         bike 0 days 00:15:00                  1.707860   

         trip_distance_meters  \
1438661            931.128902   
1433893           3604.011448   
1646587           1381.386740   
1516357           2408.581219   
1385300           1362.845608   
...                       ...   
1280469            626.191244   
1539398           1740.174844   
1453284            535.144175   
1306882            412.296430   
1358515           1707.859868   

                                            start_location  \
1438661  b'\x01\x01\x00\x00\x00!\xae\x9c\xbd3z\x1c@\xea...   
1433893  b'\x01\x01\x00\x00\x00\xec2\xfc\xa7\x1bh\x1c@\...   
1646587  b'\x01\x01\x00\x00\x00\x81\xcc\xce\xa2wZ\x1c@w...   
1516357  b'\x01\x01\x00\x00\x00X\x8f\xfbV\xebT\x1c@L\xc...   
1385300  b'\x01\x01\x00\x00\x00\xf5\xd8\x96\x01gi\x1c@[...   
...                                                    ...   
1280469  b'\x01\x01\x00\x00\x00/\x15\x1b\xf3:b\x1c@b\xd...   
1539398  b'\x01\x01\x00\x00\x00\xe9\x0b!\xe7\xfd_\x1c@\...   
1453284  b"\x01\x01\x00\x00\x00\x86\x01K\xaeba\x1c@\x1b...   
1306882  b'\x01\x01\x00\x00\x00u<f\xa02.\x1c@]\x88\xd5\...   
1358515  b'\x01\x01\x00\x00\x00\x9f\xe8\xba\xf0\x83c\x1...   

                                              end_location  start_stop_id  \
1438661  b'\x01\x01\x00\x00\x00?n\xbf|\xb2\x82\x1c@\x92...         1500.0   
1433893  b'\x01\x01\x00\x00\x00\xe8\x11\xa3\xe7\x16J\x1...

In [117]:
midday_nan_delay_next_station_station.describe()

nextbike_trips_id      nextbike_trips_start_time  \
count       1.727000e+03                           1727   
mean        3.794283e+07  2023-07-15 12:10:03.717428736   
min         3.771660e+07            2023-07-01 10:11:00   
25%         3.782991e+07            2023-07-07 11:36:00   
50%         3.794539e+07            2023-07-14 10:41:00   
75%         3.804980e+07            2023-07-22 11:51:00   
max         3.817126e+07            2023-07-31 12:01:00   
std         1.285860e+05                            NaN   

             nextbike_trips_end_time              trip_duration  \
count                           1727                       1727   
mean   2023-07-15 12:23:13.931673344  0 days 00:13:10.214244354   
min              2023-07-01 10:21:00            0 days 00:05:00   
25%              2023-07-07 11:53:30            0 days 00:10:00   
50%              2023-07-14 10:56:00            0 days 00:10:00   
75%              2023-07-22 12:01:00            0 days 00:15:00   
max              2023-07-31 12:31:00            0 days 01:55:00   
std                              NaN  0 days 00:08:26.335653658   

       trip_distance_kilometers  trip_distance_meters  start_stop_id  \
count               1727.000000           1727.000000    1727.000000   
mean                   1.340761           1340.760674    1179.937464   
min                    0.100624            100.624321      43.000000   
25%                    0.680337            680.336914     687.000000   
50%                    1.105169           1105.168521    1115.000000   
75%                    1.661401           1661.401312    1221.000000   
max                    8.017719           8017.718903    9780.000000   
std                    1.048585           1048.585375    1061.873526   

       end_stop_id  trip_duration_seconds  
count  1727.000000            1727.000000  
mean   1211.067748             790.214244  
min      43.000000             300.000000  
25%     687.000000             600.000000  
50%    1135.000000             600.000000  
75%    1221.000000             900.000000  
max    9780.000000            6900.000000  
std    1136.243256             506.335654

In [118]:
# get statistics for the tier trips that start and end at a station
get_stats(midday_nan_delay_next_station_station, ['trip_duration_seconds', 'trip_distance_kilometers'])

column                                     trip_duration_seconds  \
rows                                                        1727   
sum                                                    1364700.0   
mean                                                  790.214244   
median                                                     600.0   
mode           0    600.0
Name: trip_duration_seconds, dtype:...   
max                                                       6900.0   
min                                                        300.0   
std_dev                                               506.335654   
variance                                           256375.794165   
skewness                                                4.339915   
kurtosis                                               33.125888   
percentile_25                                              600.0   
percentile_75                                              900.0   
iqr                                                        300.0   
range                                                     6600.0   
cv                                                      0.640757   
qd                                                           0.2   
cs                                                      0.008571   
ck                                                      0.065423   
cvs                                                     0.008571   
cvk                                                     0.065423   
cvcs                                                    0.008571   
cvck                                                    0.065423   
cvcv                                                    0.640757   
cvqd                                                         0.2   
cvr                                                     8.352165   
cvm                                                          1.0   
cvmed                                                   0.759288   
cvmode         0    0.759288
Name: trip_duration_seconds, dty...   

column                                  trip_distance_kilometers  
rows                                                        1727  
sum                                                  2315.493684  
mean                                                    1.340761  
median                                                  1.105169  
mode           0    0.834842
Name: trip_distance_kilometers, ...  
max                                                     8.017719  
min                                                     0.100624  
std_dev                                                 1.048585  
variance                                                1.099531  
skewness                                                2.247342  
kurtosis                                                7.638627  
percentile_25                                           0.680337  
percentile_75                                           1.661401  
iqr                                                     0.981064  
range                                                   7.917095  
cv                                                      0.782082  
qd                                                      0.418947  
cs                                                      2.143213  
ck                                                      7.284697  
cvs                                                     2.143213  
cvk                                                     7.284697  
cvcs                                                    2.143213  
cvck                                                    7.284697  
cvcv                                                    0.782082  
cvqd                                                    0.418947  
cvr                                                     5.904928  
cvm                                                          1.0  
cvmed                                                   0.824285  
cvmode         0

In [119]:
midday_delay.describe()

route_id      agency_id     route_type     service_id  \
count  101954.000000  101954.000000  101954.000000  101954.000000   
mean      566.260667       6.005081       2.762893    3192.964180   
min        60.000000       6.000000       0.000000      43.000000   
25%       602.000000       6.000000       3.000000      64.000000   
50%       607.000000       6.000000       3.000000      64.000000   
75%       611.000000       6.000000       3.000000     130.000000   
max       843.000000      12.000000       3.000000   27690.000000   
std       149.953655       0.168811       0.809387    8578.736714   

        direction_id       shape_id        stop_id  \
count  101954.000000  101954.000000  101954.000000   
mean        0.519205    3515.953616    2338.527189   
min         0.000000       6.000000      43.000000   
25%         0.000000    1812.000000    1214.000000   
50%         1.000000    2717.000000    1441.000000   
75%         1.000000    5377.000000    1682.000000   
max         1.000000   10365.000000    9780.000000   
std         0.499633    2759.676991    2437.662294   

                 actual_arrival_time          actual_departure_time  \
count                          98618                         101954   
mean   2023-07-16 12:39:25.174004480  2023-07-16 13:31:26.822243328   
min              2023-07-01 09:59:50            2023-07-01 10:00:10   
25%              2023-07-08 11:29:00            2023-07-08 11:30:30   
50%              2023-07-17 10:23:30     2023-07-17 10:30:42.500000   
75%              2023-07-24 10:51:15            2023-07-24 10:58:30   
max              2023-07-31 12:06:00            2023-07-31 12:12:00   
std                              NaN                            NaN   

       vrs_timestamp  ...  departure_delay_float actual_arrival_time_float  \
count  101954.000000  ...          101954.000000             101954.000000   
mean    94947.891000  ...               0.654405             104312.129490   
min     75303.000000  ...               0.166667                  0.000000   
25%     90804.000000  ...               0.250000             102615.000000   
50%     93804.000000  ...               0.500000             105615.000000   
75%    101304.000000  ...               0.750000             112800.000000   
max    220309.000000  ...              43.000000             121500.000000   
std      9145.240062  ...               1.240063              19882.209322   

      actual_departure_time_float arrival_delay_span    weather_int  \
count               101954.000000           101954.0  101954.000000   
mean                107880.624939                0.0       0.131530   
min                 100010.000000                0.0       0.000000   
25%                 102930.000000                0.0       0.000000   
50%                 105845.000000                0.0       0.000000   
75%                 112930.000000                0.0       0.000000   
max                 121500.000000                0.0       2.000000   
std                   5314.617620                0.0       0.434437   

       time_span_int_arrival        weekend  time_span_int  delay_category  \
count          101954.000000  101954.000000  101954.000000   101954.000000   
mean                1.935304       0.677511       2.001815        0.629941   
min                 0.000000       0.000000       2.000000       -1.000000   
25%                 2.000000       0.000000       2.000000        0.000000   
50%                 2.000000       0.000000       2.000000        1.000000   
75%                 2.000000       1.000000       2.000000        1.000000   
max                 3.000000       3.000000       3.000000        1.000000   
std                 0.357542       0.980952       0.042559        0.546406   

       cancelled_trip  
count        101954.0  
mean              0.0  
min               0.0  
25%               0.0  
50%               0.0  
75%               0.0  
max               0.0  
std               0.0  



In [120]:
midday_no_delay.describe()

route_id     agency_id    route_type    service_id  direction_id  \
count  64182.000000  64182.000000  64182.000000  64182.000000  64182.000000   
mean     565.614004      7.017263      2.615359   5609.952775      0.498769   
min       16.000000      1.000000      0.000000     43.000000      0.000000   
25%      600.000000      6.000000      3.000000     64.000000      0.000000   
50%      608.000000      6.000000      3.000000     64.000000      0.000000   
75%      630.000000      6.000000      3.000000    151.000000      1.000000   
max      884.000000     12.000000      3.000000  29145.000000      1.000000   
std      215.816633      2.159279      1.002990  10931.881279      0.500002   

           shape_id       stop_id            actual_arrival_time  \
count  64182.000000  64182.000000                          45414   
mean    4122.014537   2169.909024  2023-07-16 10:31:32.991808512   
min        6.000000     43.000000            2023-07-01 09:59:00   
25%     2014.000000   1175.000000            2023-07-08 11:04:45   
50%     3189.000000   1384.000000            2023-07-17 10:17:45   
75%     6365.000000   1702.000000            2023-07-24 10:44:40   
max    10365.000000   9780.000000            2023-07-31 11:59:00   
std     2827.187465   2315.565686                            NaN   

               actual_departure_time  vrs_timestamp  ...  \
count                          64182   64182.000000  ...   
mean   2023-07-16 13:05:03.498255104   95015.856346  ...   
min              2023-07-01 10:00:00   80304.000000  ...   
25%              2023-07-08 11:24:00   90805.000000  ...   
50%              2023-07-17 10:28:00   93805.000000  ...   
75%    2023-07-24 10:59:48.750000128  101304.000000  ...   
max              2023-07-31 12:12:00  220309.000000  ...   
std                              NaN    8763.575976  ...   

       departure_delay_float actual_arrival_time_float  \
count           64182.000000              64182.000000   
mean                0.046124              76232.841762   
min                 0.000000                  0.000000   
25%                 0.000000                  0.000000   
50%                 0.000000             103440.000000   
75%                 0.000000             111445.000000   
max                24.000000             120200.000000   
std                 0.474705              49211.119282   

      actual_departure_time_float arrival_delay_span   weather_int  \
count                64182.000000            64182.0  64182.000000   
mean                107891.514833                0.0      0.134835   
min                  95615.000000                0.0      0.000000   
25%                 102900.000000                0.0      0.000000   
50%                 105900.000000                0.0      0.000000   
75%                 112900.000000                0.0      0.000000   
max                 121200.000000                0.0      2.000000   
std                   5303.889077                0.0      0.439392   

       time_span_int_arrival       weekend  time_span_int  delay_category  \
count           64182.000000  64182.000000   64182.000000    64182.000000   
mean                1.409554      0.712957       2.000639       -0.285890   
min                 0.000000      0.000000       1.000000       -1.000000   
25%                 0.000000      0.000000       2.000000       -1.000000   
50%                 2.000000      0.000000       2.000000        0.000000   
75%                 2.000000      2.000000       2.000000        0.000000   
max                 3.000000      3.000000       3.000000        1.000000   
std                 0.909248      0.998236       0.029794        0.466065   

       cancelled_trip  
count         64182.0  
mean              0.0  
min               0.0  
25%               0.0  
50%               0.0  
75%               0.0  
max               0.0  
std               0.0  

[8 rows x 38 columns]

In [121]:
midday_nan_delay.describe()

route_id      agency_id     route_type     service_id  \
count  127015.000000  127015.000000  127015.000000  127015.000000   
mean      550.801283       6.289832       2.659481    4270.397339   
min        16.000000       1.000000       0.000000      43.000000   
25%       601.000000       6.000000       3.000000      64.000000   
50%       607.000000       6.000000       3.000000      64.000000   
75%       613.000000       6.000000       3.000000     130.000000   
max       884.000000      12.000000       3.000000   29145.000000   
std       184.586633       1.180777       0.951636    9742.741018   

        direction_id       shape_id        stop_id actual_arrival_time  \
count  127015.000000  127015.000000  127015.000000                   0   
mean        0.494068    4028.460072    2242.708908                 NaT   
min         0.000000       6.000000      43.000000                 NaT   
25%         0.000000    1945.000000    1211.000000                 NaT   
50%         0.000000    2936.000000    1456.000000                 NaT   
75%         1.000000    6327.000000    1683.000000                 NaT   
max         1.000000   10365.000000    9780.000000                 NaT   
std         0.499967    2916.591176    2339.461798                 NaN   

      actual_departure_time  vrs_timestamp  ...  departure_delay_float  \
count                     0  127015.000000  ...                    0.0   
mean                    NaT   95428.092406  ...                    NaN   
min                     NaT   44804.000000  ...                    NaN   
25%                     NaT   90806.000000  ...                    NaN   
50%                     NaT   94304.000000  ...                    NaN   
75%                     NaT  101305.000000  ...                    NaN   
max                     NaT  220309.000000  ...                    NaN   
std                     NaN   10721.555412  ...                    NaN   

      actual_arrival_time_float actual_departure_time_float  \
count                  127015.0                    127015.0   
mean                        0.0                         0.0   
min                         0.0                         0.0   
25%                         0.0                         0.0   
50%                         0.0                         0.0   
75%                         0.0                         0.0   
max                         0.0                         0.0   
std                         0.0                         0.0   

      arrival_delay_span    weather_int  time_span_int_arrival        weekend  \
count           127015.0  127015.000000               127015.0  127015.000000   
mean                 0.0       0.114341                    0.0       0.631296   
min                  0.0       0.000000                    0.0       0.000000   
25%                  0.0       0.000000                    0.0       0.000000   
50%                  0.0       0.000000                    0.0       0.000000   
75%                  0.0       0.000000                    0.0       1.000000   
max                  0.0       2.000000                    0.0       3.000000   
std                  0.0       0.409975                    0.0       0.898524   

       time_span_int  delay_category  cancelled_trip  
count       127015.0        127015.0        127015.0  
mean             0.0            -1.0             1.0  
min              0.0            -1.0             1.0  
25%              0.0            -1.0             1.0  
50%              0.0            -1.0             1.0  
75%              0.0            -1.0             1.0  
max              0.0            -1.0             1.0  
std              0.0             0.0             0.0  

[8 rows x 38 columns]

#### Lunch Time

In [122]:
lunchtime_delay = delay[(delay['scheduled_arrival_time'].dt.hour >= 12) & (delay['scheduled_arrival_time'].dt.hour <= 14)]  
lunchtime_delay

route_id  agency_id route_short_name  route_type route_type_name  \
27734         610          6              610           3             Bus   
27735         603          6              603           3             Bus   
27737         633          6              633           3             Bus   
27743         602          6              602           3             Bus   
27745         600          6              600           3             Bus   
...           ...        ...              ...         ...             ...   
2522536       603          6              603           3             Bus   
2522538       601          6              601           3             Bus   
2522539       613          6              613           3             Bus   
2522541       630          6              630           3             Bus   
2522543       602          6              602           3             Bus   

                               agency_name  service_id  \
27734    SWB Stadtwerke Bonn Verkehrs GmbH         130   
27735    SWB Stadtwerke Bonn Verkehrs GmbH         130   
27737    SWB Stadtwerke Bonn Verkehrs GmbH         130   
27743    SWB Stadtwerke Bonn Verkehrs GmbH         130   
27745    SWB Stadtwerke Bonn Verkehrs GmbH         130   
...                                    ...         ...   
2522536  SWB Stadtwerke Bonn Verkehrs GmbH          64   
2522538  SWB Stadtwerke Bonn Verkehrs GmbH          64   
2522539  SWB Stadtwerke Bonn Verkehrs GmbH          64   
2522541  SWB Stadtwerke Bonn Verkehrs GmbH          64   
2522543  SWB Stadtwerke Bonn Verkehrs GmbH          64   

                                                   trip_id  \
27734    6100145-610-006-1756.2.21:105900-54-1_97A2983E...   
27735    6030338-603-006-2304.2.22:111100-41-1_34B6299F...   
27737    6330086-633-006-1584.2.24:114900-24-1_ED48CF7D...   
27743    6020168-602-006-9478.2.22:115800-39-1_E33A3516...   
27745    6000342-600-006-8813.2.22:115900-32-1_FD7919B3...   
...                                                    ...   
2522536  6030055-603-006-1386.2.21:143000-37-1_BC990704...   
2522538  6010124-601-006-9478.2.22:144600-44-1_B88AE9ED...   
2522539  6130112-613-006-1723.2.21:144000-28-1_34B76110...   
2522541  6300038-630-006-9478.2.22:145500-50-1_3A19AC6C...   
2522543  6020083-602-006-1307.2.22:144100-37-1_F02278B3...   

               trip_headsign  direction_id  ...  delay_span  \
27734            Duisdorf Bf             0  ...         0-5   
27735       Röttgen Schleife             1  ...         0-5   
27737       Endenich Nord Bf             1  ...         0-5   
27743                 Waldau             1  ...         0-5   
27745    Ippendorf Altenheim             1  ...         0-5   
...                      ...           ...  ...         ...   
2522536       Alte Schulstr.             0  ...         0-5   
2522538      Uniklinikum Süd             1  ...         0-5   
2522539         Giselherstr.             1  ...         0-5   
2522541      Uniklinikum Süd             1  ...         0-5   
2522543   Agnetendorfer Str.             0  ...         0-5   

         arrival_delay_span weather_int time_span_arrival  \
27734                     0           0             lunch   
27735                     0           0             lunch   
27737                     0           0             lunch   
27743                     0           0             lunch   
27745                     0           0             lunch   
...                     ...         ...               ...   
2522536                   0           0             lunch   
2522538                   0           0             lunch   
2522539                   0           0             lunch   
2522541                   0           0             lunch   
2522543                   0           0             lunch   

         time_span_int_arrival  weekend time_span time_span_int  \
27734                        3        2     lunch             3   
27735             

In [123]:
get_stats(lunchtime_delay, ['tier_trips_count', 'tier_trips_end_at_station_count', 'nextbike_trips_count', 'nextbike_trips_end_at_station_count', 'current_temp', 'current_precipitation_volume'])

/tmp/ipykernel_2575952/41814695.py:51: RuntimeWarning: invalid value encountered in scalar divide
  qd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:55: RuntimeWarning: invalid value encountered in scalar divide
  cvqd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:51: RuntimeWarning: invalid value encountered in scalar divide
  qd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:55: RuntimeWarning: invalid value encountered in scalar divide
  cvqd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:51: RuntimeWarning: invalid value encountered in scalar divide
  qd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:55: RuntimeWarning: invalid value encountered in scalar divide
  cvqd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:51: RuntimeWarning: invalid value encountered in scalar divide
  qd = iqr / (percentile_75 + percenti

column                                        tier_trips_count  \
rows                                                    167732   
sum                                                       2573   
mean                                                   0.01534   
median                                                     0.0   
mode               0    0
Name: tier_trips_count, dtype: int64   
max                                                          5   
min                                                          0   
std_dev                                               0.134881   
variance                                              0.018193   
skewness                                              10.41319   
kurtosis                                            143.190493   
percentile_25                                              0.0   
percentile_75                                              0.0   
iqr                                                        0.0   
range                                                        5   
cv                                                    8.792823   
qd                                                         NaN   
cs                                                   77.202545   
ck                                                 1061.602686   
cvs                                                  77.202545   
cvk                                                1061.602686   
cvcs                                                 77.202545   
cvck                                               1061.602686   
cvcv                                                  8.792823   
cvqd                                                       NaN   
cvr                                                 325.946366   
cvm                                                        1.0   
cvmed                                                      0.0   
cvmode         0    0.0
Name: tier_trips_count, dtype: float64   

column                           tier_trips_end_at_station_count  \
rows                                                      167732   
sum                                                         2075   
mean                                                    0.012371   
median                                                       0.0   
mode           0    0
Name: tier_trips_end_at_station_count, ...   
max                                                            4   
min                                                            0   
std_dev                                                 0.119901   
variance                                                0.014376   
skewness                                               10.975468   
kurtosis                                              143.713883   
percentile_25                                                0.0   
percentile_75                                                0.0   
iqr                                                          0.0   
range                                                          4   
cv                                                      9.692136   
qd                                                           NaN   
cs                                                     91.537985   
ck                                                    1198.60763   
cvs                                                    91.537985   
cvk                                                   1198.60763   
cvcs                                                   91.537985   
cvck                                                  1198.60763   
cvcv                                                    9.692136   
cvqd                                                         NaN   
cvr                                                   323.338795   
cvm                                                          1.0   
cvmed                                                        0.0   
cvmode         0    0.0
Name: tier_trips_end_at

In [124]:
lunchtime_delay_tier = check_micromobility_datasets('tier', lunchtime_delay)

In [125]:
lunchtime_delay_tier.describe()

tier_trips_id          tier_trips_start_time  \
count   1.781000e+03                           1781   
mean    7.973649e+08  2023-07-15 05:09:29.006176256   
min     7.822648e+08            2023-07-01 12:10:00   
25%     7.823747e+08            2023-07-07 13:45:00   
50%     7.824623e+08            2023-07-13 14:10:00   
75%     8.087377e+08            2023-07-21 14:35:00   
max     8.323115e+08            2023-07-31 15:00:00   
std     1.640237e+07                            NaN   

                 tier_trips_end_time              trip_duration  \
count                           1781                       1781   
mean   2023-07-15 05:23:30.387422464  0 days 00:14:01.381246490   
min              2023-07-01 12:25:00            0 days 00:05:00   
25%              2023-07-07 13:55:00            0 days 00:10:00   
50%              2023-07-13 14:25:00            0 days 00:10:00   
75%              2023-07-21 14:45:00            0 days 00:15:00   
max              2023-07-31 15:15:00            0 days 01:35:00   
std                              NaN  0 days 00:08:40.781716945   

       trip_distance_kilometers  trip_distance_meters  start_stop_id  \
count               1781.000000           1781.000000    1257.000000   
mean                   1.718625           1718.625102    1377.295147   
min                    0.100290            100.289988      43.000000   
25%                    0.759323            759.323232    1102.000000   
50%                    1.297086           1297.085927    1131.000000   
75%                    2.248689           2248.688905    1240.000000   
max                   11.853086          11853.086389    9703.000000   
std                    1.458466           1458.466091    1366.153785   

       end_stop_id  trip_duration_seconds  
count   986.000000            1781.000000  
mean   1321.697769             841.381246  
min      43.000000             300.000000  
25%    1102.000000             600.000000  
50%    1136.000000             600.000000  
75%    1240.000000             900.000000  
max    9703.000000            5700.000000  
std    1266.225205             520.781717

In [126]:
get_stats(lunchtime_delay_tier, ['trip_duration_seconds', 'trip_distance_kilometers'])

column                                     trip_duration_seconds  \
rows                                                        1781   
sum                                                    1498500.0   
mean                                                  841.381246   
median                                                     600.0   
mode           0    600.0
Name: trip_duration_seconds, dtype:...   
max                                                       5700.0   
min                                                        300.0   
std_dev                                               520.781717   
variance                                           271213.596704   
skewness                                                3.253327   
kurtosis                                               19.899987   
percentile_25                                              600.0   
percentile_75                                              900.0   
iqr                                                        300.0   
range                                                     5400.0   
cv                                                       0.61896   
qd                                                           0.2   
cs                                                      0.006247   
ck                                                      0.038212   
cvs                                                     0.006247   
cvk                                                     0.038212   
cvcs                                                    0.006247   
cvck                                                    0.038212   
cvcv                                                     0.61896   
cvqd                                                         0.2   
cvr                                                     6.418018   
cvm                                                          1.0   
cvmed                                                   0.713113   
cvmode         0    0.713113
Name: trip_duration_seconds, dty...   

column                                  trip_distance_kilometers  
rows                                                        1781  
sum                                                  3060.871307  
mean                                                    1.718625  
median                                                  1.297086  
mode           0        0.100290
1        0.101082
2        0...  
max                                                    11.853086  
min                                                      0.10029  
std_dev                                                 1.458466  
variance                                                2.127123  
skewness                                                2.162688  
kurtosis                                                  6.8933  
percentile_25                                           0.759323  
percentile_75                                           2.248689  
iqr                                                     1.489366  
range                                                  11.752796  
cv                                                      0.848624  
qd                                                      0.495133  
cs                                                      1.482851  
ck                                                      4.726404  
cvs                                                     1.482851  
cvk                                                     4.726404  
cvcs                                                    1.482851  
cvck                                                    4.726404  
cvcv                                                    0.848624  
cvqd                                                    0.495133  
cvr                                                     6.838488  
cvm                                                          1.0  
cvmed                                                   0.754723  
cvmode         0

In [127]:
# get entries where trips start and end at station
lunchtime_delay_tier_station_station = lunchtime_delay_tier[lunchtime_delay_tier['end_stop_id'].notna() & lunchtime_delay_tier['start_stop_id'].notna()]
lunchtime_delay_tier_station_station

tier_trips_id tier_trips_start_time tier_trips_end_time vehicle type  \
3082973      782320108   2023-07-01 12:20:00 2023-07-01 12:25:00    e-scooter   
3278736      782454329   2023-07-01 12:20:00 2023-07-01 12:35:00    e-scooter   
3226921      782407118   2023-07-01 12:20:00 2023-07-01 12:30:00    e-scooter   
3250838      782428950   2023-07-01 12:35:00 2023-07-01 12:40:00    e-scooter   
3177171      782361072   2023-07-01 12:35:00 2023-07-01 12:50:00    e-scooter   
...                ...                   ...                 ...          ...   
3439234      832221293   2023-07-31 14:15:00 2023-07-31 14:25:00    e-scooter   
3376248      832160872   2023-07-31 14:20:00 2023-07-31 14:35:00    e-scooter   
3508084      832287375   2023-07-31 14:30:00 2023-07-31 14:45:00    e-scooter   
3491611      832271568   2023-07-31 14:30:00 2023-07-31 14:45:00    e-scooter   
3482733      832263064   2023-07-31 14:35:00 2023-07-31 14:40:00    e-scooter   

          trip_duration  trip_distance_kilometers  trip_distance_meters  \
3082973 0 days 00:05:00                  0.330897            330.896717   
3278736 0 days 00:15:00                  2.391213           2391.212980   
3226921 0 days 00:10:00                  0.980556            980.556253   
3250838 0 days 00:05:00                  0.603288            603.288422   
3177171 0 days 00:15:00                  1.428714           1428.714454   
...                 ...                       ...                   ...   
3439234 0 days 00:10:00                  0.941351            941.351063   
3376248 0 days 00:15:00                  1.364117           1364.116656   
3508084 0 days 00:15:00                  2.525054           2525.054040   
3491611 0 days 00:15:00                  2.123778           2123.777937   
3482733 0 days 00:05:00                  0.574873            574.872838   

         start_stop_id              start_stop_name  \
3082973         1102.0           Bonn Friedensplatz   
3278736         1500.0   Bonn Konrad-Adenauer-Platz   
3226921         1240.0     Bonn Poppelsdorfer Platz   
3250838         1221.0            Bonn Kaufmannstr.   
3177171         1111.0  Bonn Beethovenhalle Und Swb   
...                ...                          ...   
3439234         1110.0           Bonn Wilhelmsplatz   
3376248         1620.0          Bonn Max-Bruch-Str.   
3508084         1143.0     Bonn Poppelsdorfer Allee   
3491611         1525.0           Bonn Geislar Mitte   
3482733         1162.0                Bonn Rosental   

                                         start_buffer_zone  end_stop_id  \
3082973  801621     POLYGON ((7.157885983913106 50.7227...       1104.0   
3278736  801621     POLYGON ((7.157885983913106 50.7227...       1586.0   
3226921  801621     POLYGON ((7.157885983913106 50.7227...       1242.0   
3250838  801621     POLYGON ((7.157885983913106 50.7227...       1145.0   
3177171  801621     POLYGON ((7.157885983913106 50.7227...        685.0   
...                                                    ...          ...   
3439234  801621     POLYGON ((7.157885983913106 50.7227...        686.0   
3376248  801621     POLYGON ((7.157885983913106 50.7227...       1144.0   
3508084  801621     POLYGON ((7.157885983913106 50.7227...       1620.0   
3491611  801621     POLYGON ((7.157885983913106 50.7227...       1513.0   
3482733  801621     POLYGON ((7.157885983913106 50.7227...       1111.0   

                       end_stop_name  \
3082973               Bonn Stadthaus   
3278736               Bonn Limperich   
3226921           Bonn Friedrichsruh   
3250838               Bonn Haydnstr.   
3177171               Bonn Juridicum   
...                              ...   
3439234       Bonn Universität/Markt   
3376248           Bonn Beethovenstr.   
3508084          Bonn Max-Bruch-Str.   
3491611        Bonn Rheindorfer Str.   
3482733  Bonn Beethovenhalle Und Swb   

                                           end_buffer_zone  \
3082973  801621               

In [128]:
lunchtime_delay_tier_station_station.describe()

tier_trips_id          tier_trips_start_time  \
count   8.120000e+02                            812   
mean    7.964119e+08  2023-07-14 22:38:35.394088448   
min     7.822648e+08            2023-07-01 12:20:00   
25%     7.823621e+08            2023-07-07 13:55:00   
50%     7.824539e+08            2023-07-13 12:47:30   
75%     8.087286e+08            2023-07-21 12:33:45   
max     8.323080e+08            2023-07-31 14:35:00   
std     1.597974e+07                            NaN   

              tier_trips_end_time              trip_duration  \
count                         812                        812   
mean   2023-07-14 22:51:03.916256  0 days 00:12:28.522167487   
min           2023-07-01 12:25:00            0 days 00:05:00   
25%           2023-07-07 14:03:45            0 days 00:10:00   
50%           2023-07-13 13:00:00            0 days 00:10:00   
75%           2023-07-21 12:47:30            0 days 00:15:00   
max           2023-07-31 15:05:00            0 days 01:35:00   
std                           NaN  0 days 00:07:01.242695935   

       trip_distance_kilometers  trip_distance_meters  start_stop_id  \
count                812.000000            812.000000     812.000000   
mean                   1.385220           1385.219746    1418.759852   
min                    0.100290            100.289988      43.000000   
25%                    0.630236            630.235713    1102.000000   
50%                    1.094260           1094.260078    1127.500000   
75%                    1.870408           1870.407854    1225.750000   
max                    9.093761           9093.761020    9073.000000   
std                    1.093451           1093.450670    1448.285553   

       end_stop_id  trip_duration_seconds  
count   812.000000             812.000000  
mean   1325.059113             748.522167  
min      43.000000             300.000000  
25%    1102.000000             600.000000  
50%    1143.000000             600.000000  
75%    1240.000000             900.000000  
max    9703.000000            5700.000000  
std    1226.169133             421.242696

In [129]:
# get statistics for the tier trips that start and end at a station
get_stats(lunchtime_delay_tier_station_station, ['trip_duration_seconds', 'trip_distance_kilometers'])

column                                     trip_duration_seconds  \
rows                                                         812   
sum                                                     607800.0   
mean                                                  748.522167   
median                                                     600.0   
mode           0    600.0
Name: trip_duration_seconds, dtype:...   
max                                                       5700.0   
min                                                        300.0   
std_dev                                               421.242696   
variance                                           177445.408879   
skewness                                                3.696369   
kurtosis                                                29.30998   
percentile_25                                              600.0   
percentile_75                                              900.0   
iqr                                                        300.0   
range                                                     5400.0   
cv                                                      0.562766   
qd                                                           0.2   
cs                                                      0.008775   
ck                                                       0.06958   
cvs                                                     0.008775   
cvk                                                      0.06958   
cvcs                                                    0.008775   
cvck                                                     0.06958   
cvcv                                                    0.562766   
cvqd                                                         0.2   
cvr                                                     7.214215   
cvm                                                          1.0   
cvmed                                                   0.801579   
cvmode         0    0.801579
Name: trip_duration_seconds, dty...   

column                                  trip_distance_kilometers  
rows                                                         812  
sum                                                  1124.798434  
mean                                                     1.38522  
median                                                   1.09426  
mode           0      0.100290
1      0.101082
2      0.10535...  
max                                                     9.093761  
min                                                      0.10029  
std_dev                                                 1.093451  
variance                                                1.195634  
skewness                                                2.067367  
kurtosis                                                7.208095  
percentile_25                                           0.630236  
percentile_75                                           1.870408  
iqr                                                     1.240172  
range                                                   8.993471  
cv                                                       0.78937  
qd                                                      0.495941  
cs                                                      1.890682  
ck                                                      6.592062  
cvs                                                     1.890682  
cvk                                                     6.592062  
cvcs                                                    1.890682  
cvck                                                    6.592062  
cvcv                                                     0.78937  
cvqd                                                    0.495941  
cvr                                                     6.492451  
cvm                                                          1.0  
cvmed                                                   0.789954  
cvmode         0

In [130]:
lunchtime_delay_next = check_micromobility_datasets('next', lunchtime_delay)

In [131]:
lunchtime_delay_next.describe()

nextbike_trips_id      nextbike_trips_start_time  \
count       4.715000e+03                           4715   
mean        3.793946e+07  2023-07-15 14:02:08.016967168   
min         3.771653e+07            2023-07-01 12:01:00   
25%         3.782894e+07            2023-07-08 12:11:00   
50%         3.794385e+07            2023-07-14 13:16:00   
75%         3.804683e+07            2023-07-22 13:16:00   
max         3.817172e+07            2023-07-31 15:01:00   
std         1.277794e+05                            NaN   

             nextbike_trips_end_time              trip_duration  \
count                           4715                       4715   
mean   2023-07-15 14:16:50.646871552  0 days 00:14:42.629904559   
min              2023-07-01 12:11:00            0 days 00:05:00   
25%              2023-07-08 12:26:00            0 days 00:10:00   
50%              2023-07-14 13:31:00            0 days 00:10:00   
75%              2023-07-22 13:36:00            0 days 00:15:00   
max              2023-07-31 15:21:00            0 days 02:00:00   
std                              NaN  0 days 00:10:38.854277353   

       trip_distance_kilometers  trip_distance_meters  start_stop_id  \
count               4715.000000           4715.000000    3473.000000   
mean                   1.670689           1670.688979    1249.300029   
min                    0.100321            100.320557      43.000000   
25%                    0.734656            734.655550     699.000000   
50%                    1.275934           1275.933689    1131.000000   
75%                    2.151167           2151.166988    1223.000000   
max                   14.143293          14143.293036    9780.000000   
std                    1.452201           1452.200709    1168.989917   

       end_stop_id  trip_duration_seconds  
count  2781.000000            4715.000000  
mean   1255.399856             882.629905  
min      43.000000             300.000000  
25%     688.000000             600.000000  
50%    1135.000000             600.000000  
75%    1221.000000             900.000000  
max    9702.000000            7200.000000  
std    1230.994348             638.854277

In [132]:
get_stats(lunchtime_delay_next, ['trip_duration_seconds', 'trip_distance_kilometers'])

column                                     trip_duration_seconds  \
rows                                                        4715   
sum                                                    4161600.0   
mean                                                  882.629905   
median                                                     600.0   
mode           0    600.0
Name: trip_duration_seconds, dtype:...   
max                                                       7200.0   
min                                                        300.0   
std_dev                                               638.854277   
variance                                           408134.787693   
skewness                                                 4.49258   
kurtosis                                               31.093639   
percentile_25                                              600.0   
percentile_75                                              900.0   
iqr                                                        300.0   
range                                                     6900.0   
cv                                                      0.723808   
qd                                                           0.2   
cs                                                      0.007032   
ck                                                      0.048671   
cvs                                                     0.007032   
cvk                                                     0.048671   
cvcs                                                    0.007032   
cvck                                                    0.048671   
cvcv                                                    0.723808   
cvqd                                                         0.2   
cvr                                                     7.817546   
cvm                                                          1.0   
cvmed                                                   0.679787   
cvmode         0    0.679787
Name: trip_duration_seconds, dty...   

column                                  trip_distance_kilometers  
rows                                                        4715  
sum                                                  7877.298534  
mean                                                    1.670689  
median                                                  1.275934  
mode           0    0.870199
Name: trip_distance_kilometers, ...  
max                                                    14.143293  
min                                                     0.100321  
std_dev                                                 1.452201  
variance                                                2.108887  
skewness                                                2.555936  
kurtosis                                               10.550023  
percentile_25                                           0.734656  
percentile_75                                           2.151167  
iqr                                                     1.416511  
range                                                  14.042972  
cv                                                      0.869223  
qd                                                      0.490852  
cs                                                      1.760043  
ck                                                      7.264852  
cvs                                                     1.760043  
cvk                                                     7.264852  
cvcs                                                    1.760043  
cvck                                                    7.264852  
cvcv                                                    0.869223  
cvqd                                                    0.490852  
cvr                                                     8.405498  
cvm                                                          1.0  
cvmed                                                   0.763717  
cvmode         0

In [133]:
# get entries where trips start and end at station
lunchtime_delay_next_station_station = lunchtime_delay_next[lunchtime_delay_next['end_stop_id'].notna() & lunchtime_delay_next['start_stop_id'].notna()]
lunchtime_delay_next_station_station

nextbike_trips_id nextbike_trips_start_time nextbike_trips_end_time  \
1593533           37753621       2023-07-01 12:11:00     2023-07-01 12:26:00   
1444704           37970404       2023-07-01 12:11:00     2023-07-01 12:46:00   
1585494           38127994       2023-07-01 12:11:00     2023-07-01 12:21:00   
1481167           38043638       2023-07-01 12:11:00     2023-07-01 12:21:00   
1293979           37875069       2023-07-01 12:16:00     2023-07-01 12:26:00   
...                    ...                       ...                     ...   
1624940           38158674       2023-07-31 14:51:00     2023-07-31 15:01:00   
1547892           38095768       2023-07-31 14:51:00     2023-07-31 15:01:00   
1593518           38133637       2023-07-31 14:51:00     2023-07-31 15:01:00   
1358517           37908635       2023-07-31 14:51:00     2023-07-31 15:06:00   
1286703           37871331       2023-07-31 15:01:00     2023-07-31 15:06:00   

         nextbike_trips_start_at_station  nextbike_trips_end_at_station  \
1593533                            False                          False   
1444704                            False                          False   
1585494                            False                          False   
1481167                            False                          False   
1293979                            False                          False   
...                                  ...                            ...   
1624940                            False                          False   
1547892                            False                          False   
1593518                            False                          False   
1358517                            False                          False   
1286703                            False                          False   

        vehicle type   trip_duration  trip_distance_kilometers  \
1593533         bike 0 days 00:15:00                  1.904113   
1444704         bike 0 days 00:35:00                  0.564402   
1585494         bike 0 days 00:10:00                  1.398754   
1481167         bike 0 days 00:10:00                  0.483012   
1293979         bike 0 days 00:10:00                  0.750597   
...              ...             ...                       ...   
1624940         bike 0 days 00:10:00                  1.470929   
1547892         bike 0 days 00:10:00                  0.948854   
1593518         bike 0 days 00:10:00                  0.995287   
1358517         bike 0 days 00:15:00                  1.685195   
1286703         bike 0 days 00:05:00                  0.811857   

         trip_distance_meters  \
1593533           1904.113027   
1444704            564.401609   
1585494           1398.753812   
1481167            483.011544   
1293979            750.597111   
...                       ...   
1624940           1470.928637   
1547892            948.853815   
1593518            995.287120   
1358517           1685.195181   
1286703            811.857002   

                                            start_location  \
1593533  b'\x01\x01\x00\x00\x00Z\x0f_&\x8a0\x1c@r\xa7t\...   
1444704  b'\x01\x01\x00\x00\x00j\x89\x95\xd1\xc8W\x1c@\...   
1585494  b'\x01\x01\x00\x00\x00\xa9\xa5\xb9\x15\xc2j\x1...   
1481167  b'\x01\x01\x00\x00\x00\xdf\xf9E\t\xfa[\x1c@\x8...   
1293979  b'\x01\x01\x00\x00\x00\x80\x82\x8b\x155h\x1c@\...   
...                                                    ...   
1624940  b'\x01\x01\x00\x00\x00s\xb9\xc1P\x87U\x1c@)\xe...   
1547892  b'\x01\x01\x00\x00\x00\x8bO\x010\x9eQ\x1c@\xe4...   
1593518  b'\x01\x01\x00\x00\x00O\x94\x84D\xdaf\x1c@\xa8...   
1358517  b'\x01\x01\x00\x00\x00\xfeF;n\xf8]\x1c@\x98\xa...   
1286703  b'\x01\x01\x00\x00\x00>Y1\\\x1d0\x1c@\xb0\xac4...   

                                              end_location  start_stop_id  \
1593533  b'\x01\x01\x00\x00\x00^J]2\x8eA\x1c@)\xcf\xbc\...          694.0   
1444704  b'\x01\x01\x00\x00\x00\xf5\xb8o\xb5N\\\x1c@\xe...

In [134]:
lunchtime_delay_next_station_station.describe()

nextbike_trips_id      nextbike_trips_start_time  \
count       2.263000e+03                           2263   
mean        3.794480e+07  2023-07-15 13:04:21.502430464   
min         3.771653e+07            2023-07-01 12:11:00   
25%         3.783838e+07            2023-07-08 12:31:00   
50%         3.794946e+07            2023-07-14 13:06:00   
75%         3.804950e+07            2023-07-22 12:46:00   
max         3.817156e+07            2023-07-31 15:01:00   
std         1.250515e+05                            NaN   

             nextbike_trips_end_time              trip_duration  \
count                           2263                       2263   
mean   2023-07-15 13:17:43.269995520  0 days 00:13:21.767565178   
min              2023-07-01 12:21:00            0 days 00:05:00   
25%              2023-07-08 12:46:00            0 days 00:10:00   
50%              2023-07-14 13:16:00            0 days 00:10:00   
75%              2023-07-22 12:58:30            0 days 00:15:00   
max              2023-07-31 15:06:00            0 days 02:00:00   
std                              NaN  0 days 00:08:57.543998050   

       trip_distance_kilometers  trip_distance_meters  start_stop_id  \
count               2263.000000           2263.000000    2263.000000   
mean                   1.381594           1381.594218    1278.660627   
min                    0.100321            100.320557      43.000000   
25%                    0.681051            681.050568    1102.000000   
50%                    1.122847           1122.847060    1131.000000   
75%                    1.838415           1838.415219    1221.000000   
max                    7.997983           7997.982654    9780.000000   
std                    1.052250           1052.249936    1227.327972   

       end_stop_id  trip_duration_seconds  
count  2263.000000            2263.000000  
mean   1303.105612             801.767565  
min      43.000000             300.000000  
25%     694.000000             600.000000  
50%    1140.000000             600.000000  
75%    1221.000000             900.000000  
max    9702.000000            7200.000000  
std    1295.561518             537.543998

In [135]:
# get statistics for the tier trips that start and end at a station
get_stats(lunchtime_delay_next_station_station, ['trip_duration_seconds', 'trip_distance_kilometers'])

column                                     trip_duration_seconds  \
rows                                                        2263   
sum                                                    1814400.0   
mean                                                  801.767565   
median                                                     600.0   
mode           0    600.0
Name: trip_duration_seconds, dtype:...   
max                                                       7200.0   
min                                                        300.0   
std_dev                                               537.543998   
variance                                           288953.549841   
skewness                                                 5.27889   
kurtosis                                               47.563728   
percentile_25                                              600.0   
percentile_75                                              900.0   
iqr                                                        300.0   
range                                                     6900.0   
cv                                                      0.670449   
qd                                                           0.2   
cs                                                       0.00982   
ck                                                      0.088483   
cvs                                                      0.00982   
cvk                                                     0.088483   
cvcs                                                     0.00982   
cvck                                                    0.088483   
cvcv                                                    0.670449   
cvqd                                                         0.2   
cvr                                                     8.605985   
cvm                                                          1.0   
cvmed                                                   0.748347   
cvmode         0    0.748347
Name: trip_duration_seconds, dty...   

column                                  trip_distance_kilometers  
rows                                                        2263  
sum                                                  3126.547715  
mean                                                    1.381594  
median                                                  1.122847  
mode           0    0.164644
1    0.195682
2    0.834842
Name...  
max                                                     7.997983  
min                                                     0.100321  
std_dev                                                  1.05225  
variance                                                 1.10723  
skewness                                                1.849342  
kurtosis                                                5.310278  
percentile_25                                           0.681051  
percentile_75                                           1.838415  
iqr                                                     1.157365  
range                                                   7.897662  
cv                                                       0.76162  
qd                                                      0.459369  
cs                                                      1.757512  
ck                                                      5.046594  
cvs                                                     1.757512  
cvk                                                     5.046594  
cvcs                                                    1.757512  
cvck                                                    5.046594  
cvcv                                                     0.76162  
cvqd                                                    0.459369  
cvr                                                      5.71634  
cvm                                                          1.0  
cvmed                                                   0.812718  
cvmode         0

In [136]:
lunchtime_no_delay = no_delay[(no_delay['scheduled_arrival_time'].dt.hour >= 12) & (no_delay['scheduled_arrival_time'].dt.hour <= 14)]
lunchtime_no_delay

route_id  agency_id route_short_name  route_type route_type_name  \
27730         609          6              609           3             Bus   
27740         537          8              537           3             Bus   
27741         601          6              601           3             Bus   
27742          55          1             SB55           3             Bus   
27746          63          6               63           0            Tram   
...           ...        ...              ...         ...             ...   
2522513       550          8              550           3             Bus   
2522515       884         12              884           3             Bus   
2522519       636          6              636           3             Bus   
2522524       843         12              843           3             Bus   
2522525       630          6              630           3             Bus   

                                         agency_name  service_id  \
27730              SWB Stadtwerke Bonn Verkehrs GmbH         130   
27740       RSVG Rhein-Sieg-Verkehrsgesellschaft mbH         130   
27741              SWB Stadtwerke Bonn Verkehrs GmbH         130   
27742                KVB Kölner Verkehrs-Betriebe AG       11621   
27746              SWB Stadtwerke Bonn Verkehrs GmbH          43   
...                                              ...         ...   
2522513     RSVG Rhein-Sieg-Verkehrsgesellschaft mbH          64   
2522515  RVK Regionalverkehr Köln GmbH NL Meckenheim       27690   
2522519            SWB Stadtwerke Bonn Verkehrs GmbH          64   
2522524  RVK Regionalverkehr Köln GmbH NL Meckenheim       27690   
2522525            SWB Stadtwerke Bonn Verkehrs GmbH          64   

                                                   trip_id  \
27730    6090155-609-006-1374.2.21:113200-46-1_BE47F813...   
27740    44-537-008-2140.2.21:113200-36-1_AD8D58E1-E8C6...   
27741    6010184-601-006-9478.2.22:112900-44-1_02AD41B7...   
27742    418-55-001-687.2.81:115300-23-257_E577E68A-37A...   
27746    630030-63-006-694.1.12:120000-18-1_2C515121-65...   
...                                                    ...   
2522513  76-550-008-869.2.22:142100-31-1_027CE9D0-C256-...   
2522515  38-884-012-3332.2.22:145100-16-1_901A0D02-522F...   
2522519  6360043-636-006-1584.2.21:144600-19-1_C1D0A3B2...   
2522524  37-843-012-1465.2.22:143100-39-1_9C968888-75E2...   
2522525  6300038-630-006-9478.2.22:145500-50-1_3A19AC6C...   

                    trip_headsign  direction_id  ...  delay_span  \
27730                     Gielgen             0  ...         0-5   
27740                    Bonn Hbf             0  ...           0   
27741             Uniklinikum Süd             1  ...           0   
27742               Lülsdorf Nord             0  ...           0   
27746    Bad Godesberg Stadthalle             1  ...           0   
...                           ...           ...  ...         ...   
2522513                  Bonn Hbf             1  ...           0   
2522515      Lessenich Sportplatz             1  ...           0   
2522519              Hangelar Ost             0  ...           0   
2522524         Industriepark (S)             0  ...           0   
2522525           Uniklinikum Süd             1  ...           0   

         arrival_delay_span weather_int time_span_arrival  \
27730                     0           0             lunch   
27740                     0           0             lunch   
27741                     0           0      until midday   
27742                     0           0             lunch   
27746                     0           0                 0   
...                     ...         ...               ...   
2522513                   0           0                 0   
2522515                   0           0                 0   
2522519                   0           0             lunch   
2522524                   0           0                 0   
2522525                   0       

In [137]:
get_stats(lunchtime_no_delay, ['tier_trips_count', 'tier_trips_end_at_station_count', 'nextbike_trips_count', 'nextbike_trips_end_at_station_count', 'current_temp', 'current_precipitation_volume'])

/tmp/ipykernel_2575952/41814695.py:51: RuntimeWarning: invalid value encountered in scalar divide
  qd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:55: RuntimeWarning: invalid value encountered in scalar divide
  cvqd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:51: RuntimeWarning: invalid value encountered in scalar divide
  qd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:55: RuntimeWarning: invalid value encountered in scalar divide
  cvqd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:51: RuntimeWarning: invalid value encountered in scalar divide
  qd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:55: RuntimeWarning: invalid value encountered in scalar divide
  cvqd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:51: RuntimeWarning: invalid value encountered in scalar divide
  qd = iqr / (percentile_75 + percenti

column                                        tier_trips_count  \
rows                                                    105922   
sum                                                       3718   
mean                                                  0.035101   
median                                                     0.0   
mode               0    0
Name: tier_trips_count, dtype: int64   
max                                                          5   
min                                                          0   
std_dev                                               0.212289   
variance                                              0.045067   
skewness                                              7.786874   
kurtosis                                              86.77914   
percentile_25                                              0.0   
percentile_75                                              0.0   
iqr                                                        0.0   
range                                                        5   
cv                                                     6.04789   
qd                                                         NaN   
cs                                                   36.680563   
ck                                                  408.778662   
cvs                                                  36.680563   
cvk                                                 408.778662   
cvcs                                                 36.680563   
cvck                                                408.778662   
cvcv                                                   6.04789   
cvqd                                                       NaN   
cvr                                                 142.444863   
cvm                                                        1.0   
cvmed                                                      0.0   
cvmode         0    0.0
Name: tier_trips_count, dtype: float64   

column                           tier_trips_end_at_station_count  \
rows                                                      105922   
sum                                                         2904   
mean                                                    0.027416   
median                                                       0.0   
mode           0    0
Name: tier_trips_end_at_station_count, ...   
max                                                            3   
min                                                            0   
std_dev                                                 0.180695   
variance                                                0.032651   
skewness                                                7.587406   
kurtosis                                               69.077199   
percentile_25                                                0.0   
percentile_75                                                0.0   
iqr                                                          0.0   
range                                                          3   
cv                                                      6.590753   
qd                                                           NaN   
cs                                                     41.990188   
ck                                                    382.286733   
cvs                                                    41.990188   
cvk                                                   382.286733   
cvcs                                                   41.990188   
cvck                                                  382.286733   
cvcv                                                    6.590753   
cvqd                                                         NaN   
cvr                                                   109.423554   
cvm                                                          1.0   
cvmed                                                        0.0   
cvmode         0    0.0
Name: tier_trips_end_at

In [138]:
lunchtime_no_delay_tier = check_micromobility_datasets('tier', lunchtime_no_delay)

In [139]:
lunchtime_no_delay_tier.describe()

tier_trips_id          tier_trips_start_time  \
count   1.472000e+03                           1472   
mean    7.970243e+08  2023-07-15 04:43:55.190217216   
min     7.822647e+08            2023-07-01 12:00:00   
25%     7.823709e+08            2023-07-07 14:33:45   
50%     7.824598e+08            2023-07-13 13:20:00   
75%     8.087299e+08            2023-07-22 13:20:00   
max     8.323082e+08            2023-07-31 14:50:00   
std     1.614609e+07                            NaN   

                 tier_trips_end_time              trip_duration  \
count                           1472                       1472   
mean   2023-07-15 04:57:50.380434944  0 days 00:13:55.190217391   
min              2023-07-01 12:20:00            0 days 00:05:00   
25%              2023-07-07 14:48:45            0 days 00:10:00   
50%              2023-07-13 13:42:30            0 days 00:10:00   
75%              2023-07-22 13:31:15            0 days 00:15:00   
max              2023-07-31 15:15:00            0 days 01:35:00   
std                              NaN  0 days 00:08:53.575058568   

       trip_distance_kilometers  trip_distance_meters  start_stop_id  \
count               1472.000000           1472.000000    1162.000000   
mean                   1.733064           1733.064311    1142.179862   
min                    0.100290            100.289988      43.000000   
25%                    0.773179            773.178837     687.000000   
50%                    1.320648           1320.648420    1106.000000   
75%                    2.207065           2207.064701    1240.750000   
max                   12.396107          12396.107334    9703.000000   
std                    1.489875           1489.875274    1063.679928   

       end_stop_id  trip_duration_seconds  
count   743.000000            1472.000000  
mean   1378.701211             835.190217  
min      43.000000             300.000000  
25%    1103.000000             600.000000  
50%    1150.000000             600.000000  
75%    1245.000000             900.000000  
max    9703.000000            5700.000000  
std    1350.229416             533.575059

In [140]:
get_stats(lunchtime_no_delay_tier, ['trip_duration_seconds', 'trip_distance_kilometers'])

column                                     trip_duration_seconds  \
rows                                                        1472   
sum                                                    1229400.0   
mean                                                  835.190217   
median                                                     600.0   
mode           0    600.0
Name: trip_duration_seconds, dtype:...   
max                                                       5700.0   
min                                                        300.0   
std_dev                                               533.575059   
variance                                           284702.343127   
skewness                                                3.300968   
kurtosis                                               18.084761   
percentile_25                                              600.0   
percentile_75                                              900.0   
iqr                                                        300.0   
range                                                     5400.0   
cv                                                      0.638867   
qd                                                           0.2   
cs                                                      0.006187   
ck                                                      0.033894   
cvs                                                     0.006187   
cvk                                                     0.033894   
cvcs                                                    0.006187   
cvck                                                    0.033894   
cvcv                                                    0.638867   
cvqd                                                         0.2   
cvr                                                     6.465593   
cvm                                                          1.0   
cvmed                                                   0.718399   
cvmode         0    0.718399
Name: trip_duration_seconds, dty...   

column                                  trip_distance_kilometers  
rows                                                        1472  
sum                                                  2551.070665  
mean                                                    1.733064  
median                                                  1.320648  
mode           0        0.100290
1        0.102492
2        0...  
max                                                    12.396107  
min                                                      0.10029  
std_dev                                                 1.489875  
variance                                                2.219728  
skewness                                                2.238511  
kurtosis                                                7.588522  
percentile_25                                           0.773179  
percentile_75                                           2.207065  
iqr                                                     1.433886  
range                                                  12.295817  
cv                                                      0.859677  
qd                                                       0.48113  
cs                                                      1.502482  
ck                                                      5.093394  
cvs                                                     1.502482  
cvk                                                     5.093394  
cvcs                                                    1.502482  
cvck                                                    5.093394  
cvcv                                                    0.859677  
cvqd                                                     0.48113  
cvr                                                     7.094842  
cvm                                                          1.0  
cvmed                                                   0.762031  
cvmode         0

In [141]:
# get entries where trips start and end at station
lunchtime_no_delay_tier_station_station = lunchtime_no_delay_tier[lunchtime_no_delay_tier['end_stop_id'].notna() & lunchtime_no_delay_tier['start_stop_id'].notna()]
lunchtime_no_delay_tier_station_station

tier_trips_id tier_trips_start_time tier_trips_end_time vehicle type  \
3064561      782314064   2023-07-01 12:15:00 2023-07-01 12:25:00    e-scooter   
3278736      782454329   2023-07-01 12:20:00 2023-07-01 12:35:00    e-scooter   
3238616      782417783   2023-07-01 12:20:00 2023-07-01 12:30:00    e-scooter   
3250838      782428950   2023-07-01 12:35:00 2023-07-01 12:40:00    e-scooter   
2984627      782289643   2023-07-01 12:55:00 2023-07-01 13:15:00    e-scooter   
...                ...                   ...                 ...          ...   
3386231      832170491   2023-07-31 14:10:00 2023-07-31 14:25:00    e-scooter   
3439234      832221293   2023-07-31 14:15:00 2023-07-31 14:25:00    e-scooter   
3441793      832223754   2023-07-31 14:20:00 2023-07-31 14:30:00    e-scooter   
3523189      832301874   2023-07-31 14:25:00 2023-07-31 14:40:00    e-scooter   
3419833      832202667   2023-07-31 14:50:00 2023-07-31 14:55:00    e-scooter   

          trip_duration  trip_distance_kilometers  trip_distance_meters  \
3064561 0 days 00:10:00                  2.363972           2363.972459   
3278736 0 days 00:15:00                  2.391213           2391.212980   
3238616 0 days 00:10:00                  0.864217            864.217127   
3250838 0 days 00:05:00                  0.603288            603.288422   
2984627 0 days 00:20:00                  2.795566           2795.566453   
...                 ...                       ...                   ...   
3386231 0 days 00:15:00                  2.302870           2302.870354   
3439234 0 days 00:10:00                  0.941351            941.351063   
3441793 0 days 00:10:00                  1.026721           1026.720700   
3523189 0 days 00:15:00                  1.388031           1388.030832   
3419833 0 days 00:05:00                  1.108613           1108.612542   

         start_stop_id                            start_stop_name  \
3064561         2667.0  Bonn Brüdergasse/Bertha-Von-Suttner-Platz   
3278736         1500.0                 Bonn Konrad-Adenauer-Platz   
3238616          687.0                                   Bonn Hbf   
3250838         1221.0                          Bonn Kaufmannstr.   
2984627         1115.0  Bonn Bertha-Von-Suttner-Pl./Beethovenhaus   
...                ...                                        ...   
3386231         1102.0                         Bonn Friedensplatz   
3439234         1110.0                         Bonn Wilhelmsplatz   
3441793         1500.0                 Bonn Konrad-Adenauer-Platz   
3523189          687.0                                   Bonn Hbf   
3419833          687.0                                   Bonn Hbf   

                                         start_buffer_zone  end_stop_id  \
3064561  801621     POLYGON ((7.157885983913106 50.7227...       1504.0   
3278736  801621     POLYGON ((7.157885983913106 50.7227...       1586.0   
3238616  801621     POLYGON ((7.157885983913106 50.7227...       1115.0   
3250838  801621     POLYGON ((7.157885983913106 50.7227...       1145.0   
2984627  801621     POLYGON ((7.157885983913106 50.7227...        692.0   
...                                                    ...          ...   
3386231  801621     POLYGON ((7.157885983913106 50.7227...       1500.0   
3439234  801621     POLYGON ((7.157885983913106 50.7227...        686.0   
3441793  801621     POLYGON ((7.157885983913106 50.7227...       1504.0   
3523189  801621     POLYGON ((7.157885983913106 50.7227...       1136.0   
3419833  801621     POLYGON ((7.157885983913106 50.7227...       1140.0   

                                     end_stop_name  \
3064561                              Bonn Beuel Bf   
3278736                             Bonn Limperich   
3238616  Bonn Bertha-Von-Suttner-Pl./Beethovenhaus   
3250838                             Bonn Haydnstr.   
2984627               Bonn Heussallee/Museumsmeile   
...                                            ...   
3386231                 Bon

In [142]:
lunchtime_no_delay_tier_station_station.describe()

tier_trips_id          tier_trips_start_time  \
count   6.570000e+02                            657   
mean    7.964254e+08  2023-07-15 05:19:28.493150720   
min     7.822648e+08            2023-07-01 12:15:00   
25%     7.823644e+08            2023-07-08 12:25:00   
50%     7.824552e+08            2023-07-13 12:50:00   
75%     8.087221e+08            2023-07-22 13:20:00   
max     8.323082e+08            2023-07-31 14:50:00   
std     1.569428e+07                            NaN   

                 tier_trips_end_time              trip_duration  \
count                            657                        657   
mean   2023-07-15 05:31:48.219177984  0 days 00:12:19.726027397   
min              2023-07-01 12:25:00            0 days 00:05:00   
25%              2023-07-08 12:35:00            0 days 00:10:00   
50%              2023-07-13 13:00:00            0 days 00:10:00   
75%              2023-07-22 13:30:00            0 days 00:15:00   
max              2023-07-31 14:55:00            0 days 00:50:00   
std                              NaN  0 days 00:06:00.159921044   

       trip_distance_kilometers  trip_distance_meters  start_stop_id  \
count                657.000000            657.000000     657.000000   
mean                   1.451600           1451.600226    1204.337900   
min                    0.100290            100.289988      43.000000   
25%                    0.688454            688.454209     687.000000   
50%                    1.175171           1175.171482    1115.000000   
75%                    1.920650           1920.649697    1221.000000   
max                    7.187617           7187.617396    9703.000000   
std                    1.114047           1114.046953    1121.662281   

       end_stop_id  trip_duration_seconds  
count   657.000000             657.000000  
mean   1395.217656             739.726027  
min      43.000000             300.000000  
25%    1103.000000             600.000000  
50%    1150.000000             600.000000  
75%    1240.000000             900.000000  
max    9703.000000            3000.000000  
std    1363.954198             360.159921

In [143]:
# get statistics for the tier trips that start and end at a station
get_stats(lunchtime_no_delay_tier_station_station, ['trip_duration_seconds', 'trip_distance_kilometers'])

column                                     trip_duration_seconds  \
rows                                                         657   
sum                                                     486000.0   
mean                                                  739.726027   
median                                                     600.0   
mode           0    600.0
Name: trip_duration_seconds, dtype:...   
max                                                       3000.0   
min                                                        300.0   
std_dev                                               360.159921   
variance                                           129715.168727   
skewness                                                1.933981   
kurtosis                                                6.910896   
percentile_25                                              600.0   
percentile_75                                              900.0   
iqr                                                        300.0   
range                                                     2700.0   
cv                                                      0.486883   
qd                                                           0.2   
cs                                                       0.00537   
ck                                                      0.019188   
cvs                                                      0.00537   
cvk                                                     0.019188   
cvcs                                                     0.00537   
cvck                                                    0.019188   
cvcv                                                    0.486883   
cvqd                                                         0.2   
cvr                                                         3.65   
cvm                                                          1.0   
cvmed                                                   0.811111   
cvmode         0    0.811111
Name: trip_duration_seconds, dty...   

column                                  trip_distance_kilometers  
rows                                                         657  
sum                                                   953.701348  
mean                                                      1.4516  
median                                                  1.175171  
mode           0      0.100290
1      0.102492
2      0.10340...  
max                                                     7.187617  
min                                                      0.10029  
std_dev                                                 1.114047  
variance                                                1.241101  
skewness                                                1.684126  
kurtosis                                                3.981352  
percentile_25                                           0.688454  
percentile_75                                            1.92065  
iqr                                                     1.232195  
range                                                   7.087327  
cv                                                      0.767461  
qd                                                      0.472268  
cs                                                      1.511719  
ck                                                      3.573774  
cvs                                                     1.511719  
cvk                                                     3.573774  
cvcs                                                    1.511719  
cvck                                                    3.573774  
cvcv                                                    0.767461  
cvqd                                                    0.472268  
cvr                                                     4.882424  
cvm                                                          1.0  
cvmed                                                    0.80957  
cvmode         0

In [144]:
lunchtime_no_delay_next = check_micromobility_datasets('next', lunchtime_no_delay)

In [145]:
lunchtime_no_delay_next.describe()

nextbike_trips_id      nextbike_trips_start_time  \
count       3.556000e+03                           3556   
mean        3.794086e+07  2023-07-15 11:42:29.679415040   
min         3.771653e+07            2023-07-01 12:01:00   
25%         3.783066e+07            2023-07-07 14:24:45   
50%         3.794253e+07            2023-07-14 13:16:00   
75%         3.804923e+07            2023-07-22 13:57:15   
max         3.817169e+07            2023-07-31 15:01:00   
std         1.276837e+05                            NaN   

             nextbike_trips_end_time              trip_duration  \
count                           3556                       3556   
mean   2023-07-15 11:57:03.357705472  0 days 00:14:33.678290213   
min              2023-07-01 12:16:00            0 days 00:05:00   
25%              2023-07-07 14:41:00            0 days 00:10:00   
50%              2023-07-14 13:31:00            0 days 00:10:00   
75%              2023-07-22 14:11:00            0 days 00:15:00   
max              2023-07-31 15:16:00            0 days 02:00:00   
std                              NaN  0 days 00:10:06.183859434   

       trip_distance_kilometers  trip_distance_meters  start_stop_id  \
count               3556.000000           3556.000000    2998.000000   
mean                   1.643442           1643.441564    1034.557038   
min                    0.100332            100.332419      43.000000   
25%                    0.743150            743.150024     687.000000   
50%                    1.268576           1268.576013    1103.000000   
75%                    2.034736           2034.736176    1221.000000   
max                   13.602096          13602.096364    9780.000000   
std                    1.424303           1424.303275     741.736764   

       end_stop_id  trip_duration_seconds  
count  2054.000000            3556.000000  
mean   1285.841772             873.678290  
min      43.000000             300.000000  
25%     699.000000             600.000000  
50%    1140.000000             600.000000  
75%    1221.000000             900.000000  
max    9780.000000            7200.000000  
std    1302.101168             606.183859

In [146]:
get_stats(lunchtime_no_delay_next, ['trip_duration_seconds', 'trip_distance_kilometers'])

column                                     trip_duration_seconds  \
rows                                                        3556   
sum                                                    3106800.0   
mean                                                   873.67829   
median                                                     600.0   
mode           0    600.0
Name: trip_duration_seconds, dtype:...   
max                                                       7200.0   
min                                                        300.0   
std_dev                                               606.183859   
variance                                           367458.871439   
skewness                                                4.135683   
kurtosis                                               27.539161   
percentile_25                                              600.0   
percentile_75                                              900.0   
iqr                                                        300.0   
range                                                     6900.0   
cv                                                       0.69383   
qd                                                           0.2   
cs                                                      0.006822   
ck                                                       0.04543   
cvs                                                     0.006822   
cvk                                                      0.04543   
cvcs                                                    0.006822   
cvck                                                     0.04543   
cvcv                                                     0.69383   
cvqd                                                         0.2   
cvr                                                     7.897644   
cvm                                                          1.0   
cvmed                                                   0.686752   
cvmode         0    0.686752
Name: trip_duration_seconds, dty...   

column                                  trip_distance_kilometers  
rows                                                        3556  
sum                                                  5844.078202  
mean                                                    1.643442  
median                                                  1.268576  
mode           0    0.376674
Name: trip_distance_kilometers, ...  
max                                                    13.602096  
min                                                     0.100332  
std_dev                                                 1.424303  
variance                                                 2.02864  
skewness                                                2.525246  
kurtosis                                               10.104118  
percentile_25                                            0.74315  
percentile_75                                           2.034736  
iqr                                                     1.291586  
range                                                  13.501764  
cv                                                      0.866659  
qd                                                      0.464953  
cs                                                      1.772969  
ck                                                      7.094078  
cvs                                                     1.772969  
cvk                                                     7.094078  
cvcs                                                    1.772969  
cvck                                                    7.094078  
cvcv                                                    0.866659  
cvqd                                                    0.464953  
cvr                                                     8.215542  
cvm                                                          1.0  
cvmed                                                   0.771902  
cvmode         0

In [147]:
# get entries where trips start and end at station
lunchtime_no_delay_next_station_station = lunchtime_no_delay_next[lunchtime_no_delay_next['end_stop_id'].notna() & lunchtime_no_delay_next['start_stop_id'].notna()]
lunchtime_no_delay_next_station_station

nextbike_trips_id nextbike_trips_start_time nextbike_trips_end_time  \
1288123           37837777       2023-07-01 12:06:00     2023-07-01 12:21:00   
1524518           38077625       2023-07-01 12:06:00     2023-07-01 12:26:00   
1585494           38127994       2023-07-01 12:11:00     2023-07-01 12:21:00   
1593533           37753621       2023-07-01 12:11:00     2023-07-01 12:26:00   
1296659           37842775       2023-07-01 12:11:00     2023-07-01 12:21:00   
...                    ...                       ...                     ...   
1358517           37908635       2023-07-31 14:51:00     2023-07-31 15:06:00   
1301122           37878906       2023-07-31 14:56:00     2023-07-31 15:06:00   
1467817           37975497       2023-07-31 14:56:00     2023-07-31 15:06:00   
1533238           38084253       2023-07-31 14:56:00     2023-07-31 15:16:00   
1506797           38063030       2023-07-31 15:01:00     2023-07-31 15:16:00   

         nextbike_trips_start_at_station  nextbike_trips_end_at_station  \
1288123                             True                          False   
1524518                             True                          False   
1585494                            False                          False   
1593533                            False                          False   
1296659                             True                          False   
...                                  ...                            ...   
1358517                            False                          False   
1301122                            False                          False   
1467817                            False                          False   
1533238                            False                          False   
1506797                            False                          False   

        vehicle type   trip_duration  trip_distance_kilometers  \
1288123         bike 0 days 00:15:00                  3.492510   
1524518         bike 0 days 00:20:00                  1.235203   
1585494         bike 0 days 00:10:00                  1.398754   
1593533         bike 0 days 00:15:00                  1.904113   
1296659         bike 0 days 00:10:00                  1.013501   
...              ...             ...                       ...   
1358517         bike 0 days 00:15:00                  1.685195   
1301122         bike 0 days 00:10:00                  1.354012   
1467817         bike 0 days 00:10:00                  0.443949   
1533238         bike 0 days 00:20:00                  1.684933   
1506797         bike 0 days 00:15:00                  3.304795   

         trip_distance_meters  \
1288123           3492.510346   
1524518           1235.202730   
1585494           1398.753812   
1593533           1904.113027   
1296659           1013.501489   
...                       ...   
1358517           1685.195181   
1301122           1354.011648   
1467817            443.949088   
1533238           1684.933448   
1506797           3304.795051   

                                            start_location  \
1288123  b'\x01\x01\x00\x00\x007m\xc6i\x88z\x1c@\xb0\xf...   
1524518  b'\x01\x01\x00\x00\x00t\xef\xe1\x92\xe3\x9e\x1...   
1585494  b'\x01\x01\x00\x00\x00\xa9\xa5\xb9\x15\xc2j\x1...   
1593533  b'\x01\x01\x00\x00\x00Z\x0f_&\x8a0\x1c@r\xa7t\...   
1296659  b'\x01\x01\x00\x00\x00\xfa\xb6`\xa9.0\x1c@\xe9...   
...                                                    ...   
1358517  b'\x01\x01\x00\x00\x00\xfeF;n\xf8]\x1c@\x98\xa...   
1301122  b'\x01\x01\x00\x00\x00\xa1\x9f\xa9\xd7-b\x1c@\...   
1467817  b'\x01\x01\x00\x00\x00)\x94\x85\xaf\xafe\x1c@h...   
1533238  b'\x01\x01\x00\x00\x00\xccD\x11R\xb7c\x1c@>w\x...   
1506797  b'\x01\x01\x00\x00\x00\xdf\xf8\xda3Kb\x1c@\x9e...   

                                              end_location  start_stop_id  \
1288123  b'\x01\x01\x00\x00\x00\x92Z(\x99\x9cZ\x1c@QO\x...         1500.0   
1524518  b'\x01\x01\x00\x00\x00\x84\xd5X\xc2\xda\xa8\x1...

In [148]:
lunchtime_no_delay_next_station_station.describe()

nextbike_trips_id      nextbike_trips_start_time  \
count       1.842000e+03                           1842   
mean        3.794488e+07  2023-07-15 08:27:12.801303040   
min         3.771657e+07            2023-07-01 12:06:00   
25%         3.783898e+07            2023-07-07 13:51:00   
50%         3.794805e+07            2023-07-14 12:51:00   
75%         3.804683e+07            2023-07-22 13:26:00   
max         3.817157e+07            2023-07-31 15:01:00   
std         1.248833e+05                            NaN   

             nextbike_trips_end_time              trip_duration  \
count                           1842                       1842   
mean   2023-07-15 08:40:32.638436352  0 days 00:13:19.837133550   
min              2023-07-01 12:16:00            0 days 00:05:00   
25%              2023-07-07 14:01:00            0 days 00:10:00   
50%              2023-07-14 12:58:30            0 days 00:10:00   
75%              2023-07-22 13:46:00            0 days 00:15:00   
max              2023-07-31 15:16:00            0 days 02:00:00   
std                              NaN  0 days 00:08:34.921272593   

       trip_distance_kilometers  trip_distance_meters  start_stop_id  \
count               1842.000000           1842.000000    1842.000000   
mean                   1.394627           1394.626839    1059.765472   
min                    0.100332            100.332419      43.000000   
25%                    0.700508            700.507633     687.000000   
50%                    1.163761           1163.761022    1106.000000   
75%                    1.688256           1688.256284    1221.000000   
max                    8.605918           8605.918179    9703.000000   
std                    1.101239           1101.239380     736.282611   

       end_stop_id  trip_duration_seconds  
count  1842.000000            1842.000000  
mean   1318.180782             799.837134  
min      43.000000             300.000000  
25%    1102.000000             600.000000  
50%    1141.000000             600.000000  
75%    1221.000000             900.000000  
max    9780.000000            7200.000000  
std    1339.697175             514.921273

In [149]:
# get statistics for the tier trips that start and end at a station
get_stats(lunchtime_no_delay_next_station_station, ['trip_duration_seconds', 'trip_distance_kilometers'])

column                                     trip_duration_seconds  \
rows                                                        1842   
sum                                                    1473300.0   
mean                                                  799.837134   
median                                                     600.0   
mode           0    600.0
Name: trip_duration_seconds, dtype:...   
max                                                       7200.0   
min                                                        300.0   
std_dev                                               514.921273   
variance                                           265143.916969   
skewness                                                4.681321   
kurtosis                                               39.155119   
percentile_25                                              600.0   
percentile_75                                              900.0   
iqr                                                        300.0   
range                                                     6900.0   
cv                                                      0.643783   
qd                                                           0.2   
cs                                                      0.009091   
ck                                                      0.076041   
cvs                                                     0.009091   
cvk                                                     0.076041   
cvcs                                                    0.009091   
cvck                                                    0.076041   
cvcv                                                    0.643783   
cvqd                                                         0.2   
cvr                                                     8.626756   
cvm                                                          1.0   
cvmed                                                   0.750153   
cvmode         0    0.750153
Name: trip_duration_seconds, dty...   

column                                  trip_distance_kilometers  
rows                                                        1842  
sum                                                  2568.902638  
mean                                                    1.394627  
median                                                  1.163761  
mode           0    0.222838
Name: trip_distance_kilometers, ...  
max                                                     8.605918  
min                                                     0.100332  
std_dev                                                 1.101239  
variance                                                1.212728  
skewness                                                2.187125  
kurtosis                                                7.159943  
percentile_25                                           0.700508  
percentile_75                                           1.688256  
iqr                                                     0.987749  
range                                                   8.505586  
cv                                                       0.78963  
qd                                                      0.413498  
cs                                                      1.986058  
ck                                                      6.501714  
cvs                                                     1.986058  
cvk                                                     6.501714  
cvcs                                                    1.986058  
cvck                                                    6.501714  
cvcv                                                     0.78963  
cvqd                                                    0.413498  
cvr                                                     6.098826  
cvm                                                          1.0  
cvmed                                                   0.834461  
cvmode         0

In [150]:
lunchtime_nan_delay = nan_delay[(nan_delay['scheduled_arrival_time'].dt.hour >= 12) & (nan_delay['scheduled_arrival_time'].dt.hour <= 14)]    
lunchtime_nan_delay

route_id  agency_id route_short_name  route_type route_type_name  \
27731         600          6              600           3             Bus   
27732         632          6              632           3             Bus   
27733         609          6              609           3             Bus   
27736         611          6              611           3             Bus   
27738         601          6              601           3             Bus   
...           ...        ...              ...         ...             ...   
2522544        65          6               65           0            Tram   
2522545        66          6               66           0            Tram   
2522546       551          8              551           3             Bus   
2522547       601          6              601           3             Bus   
2522548       611          6              611           3             Bus   

                                      agency_name  service_id  \
27731           SWB Stadtwerke Bonn Verkehrs GmbH         130   
27732           SWB Stadtwerke Bonn Verkehrs GmbH         130   
27733           SWB Stadtwerke Bonn Verkehrs GmbH         130   
27736           SWB Stadtwerke Bonn Verkehrs GmbH         130   
27738           SWB Stadtwerke Bonn Verkehrs GmbH         130   
...                                           ...         ...   
2522544         SWB Stadtwerke Bonn Verkehrs GmbH       26825   
2522545         SWB Stadtwerke Bonn Verkehrs GmbH       27312   
2522546  RSVG Rhein-Sieg-Verkehrsgesellschaft mbH          64   
2522547         SWB Stadtwerke Bonn Verkehrs GmbH          64   
2522548         SWB Stadtwerke Bonn Verkehrs GmbH          64   

                                                   trip_id  \
27731    6000340-600-006-8813.2.22:113900-32-1_85099653...   
27732    6320202-632-006-8832.2.23:115400-26-1_65752141...   
27733    6090153-609-006-1374.2.21:111200-46-1_99C4D783...   
27736    6110173-611-006-1723.2.21:110600-60-1_08B0A41C...   
27738    6010193-601-006-1293.2.21:114100-46-1_0C1A9FDD...   
...                                                    ...   
2522544  651094-65-006-1406.1.12:145400-24-179_A9507307...   
2522545  661268-66-006-1811.1.12:142700-32-1_EA9CFD85-B...   
2522546  189-551-008-2071.2.22:141100-34-157_C4F2270E-9...   
2522547  6010103-601-006-1293.2.21:141900-46-1_EC04E41C...   
2522548  6110100-611-006-1338.2.21:134000-58-1_CC5351C4...   

                       trip_headsign  direction_id  ...  delay_span  \
27731            Ippendorf Altenheim             1  ...           0   
27732                Uniklinikum Süd             1  ...           0   
27733                        Gielgen             0  ...           0   
27736           Lessenich Sportplatz             0  ...           0   
27738             Agnetendorfer Str.             0  ...           0   
...                              ...           ...  ...         ...   
2522544  Oberkassel Süd/Römlinghoven             1  ...           0   
2522545          Clemens-August-Str.             1  ...           0   
2522546                     Bonn Hbf             1  ...           0   
2522547           Agnetendorfer Str.             0  ...           0   
2522548                    Pappelweg             1  ...           0   

         arrival_delay_span weather_int time_span_arrival  \
27731                     0           0                 0   
27732                     0           0                 0   
27733                     0           0                 0   
27736                     0           0                 0   
27738                     0           0                 0   
...                     ...         ...               ...   
2522544                   0           0                 0   
2522545                   0           0                 0   
2522546                   0           0                 0   
2522547                   0           0                 0   
2522548                   0       

In [151]:
get_stats(lunchtime_nan_delay, ['tier_trips_count', 'tier_trips_end_at_station_count', 'nextbike_trips_count', 'nextbike_trips_end_at_station_count', 'current_temp', 'current_precipitation_volume'])

/tmp/ipykernel_2575952/41814695.py:51: RuntimeWarning: invalid value encountered in scalar divide
  qd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:55: RuntimeWarning: invalid value encountered in scalar divide
  cvqd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:51: RuntimeWarning: invalid value encountered in scalar divide
  qd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:55: RuntimeWarning: invalid value encountered in scalar divide
  cvqd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:51: RuntimeWarning: invalid value encountered in scalar divide
  qd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:55: RuntimeWarning: invalid value encountered in scalar divide
  cvqd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:51: RuntimeWarning: invalid value encountered in scalar divide
  qd = iqr / (percentile_75 + percenti

column                                        tier_trips_count  \
rows                                                    186150   
sum                                                       3940   
mean                                                  0.021166   
median                                                     0.0   
mode               0    0
Name: tier_trips_count, dtype: int64   
max                                                          5   
min                                                          0   
std_dev                                                0.15901   
variance                                              0.025284   
skewness                                              8.967778   
kurtosis                                            106.590545   
percentile_25                                              0.0   
percentile_75                                              0.0   
iqr                                                        0.0   
range                                                        5   
cv                                                    7.512603   
qd                                                         NaN   
cs                                                    56.39768   
ck                                                  670.339893   
cvs                                                   56.39768   
cvk                                                 670.339893   
cvcs                                                  56.39768   
cvck                                                670.339893   
cvcv                                                  7.512603   
cvqd                                                       NaN   
cvr                                                 236.230964   
cvm                                                        1.0   
cvmed                                                      0.0   
cvmode         0    0.0
Name: tier_trips_count, dtype: float64   

column                           tier_trips_end_at_station_count  \
rows                                                      186150   
sum                                                         3155   
mean                                                    0.016949   
median                                                       0.0   
mode           0    0
Name: tier_trips_end_at_station_count, ...   
max                                                            4   
min                                                            0   
std_dev                                                 0.138864   
variance                                                0.019283   
skewness                                                9.187659   
kurtosis                                              100.537259   
percentile_25                                                0.0   
percentile_75                                                0.0   
iqr                                                          0.0   
range                                                          4   
cv                                                      8.193169   
qd                                                           NaN   
cs                                                      66.16322   
ck                                                    724.000373   
cvs                                                     66.16322   
cvk                                                   724.000373   
cvcs                                                    66.16322   
cvck                                                  724.000373   
cvcv                                                    8.193169   
cvqd                                                         NaN   
cvr                                                   236.006339   
cvm                                                          1.0   
cvmed                                                        0.0   
cvmode         0    0.0
Name: tier_trips_end_at

In [152]:
lunchtime_nan_delay_tier = check_micromobility_datasets('tier', lunchtime_nan_delay)

In [153]:
lunchtime_nan_delay_tier.describe()

tier_trips_id          tier_trips_start_time  \
count   2.085000e+03                           2085   
mean    7.987788e+08  2023-07-15 15:27:04.172662016   
min     7.822648e+08            2023-07-01 12:10:00   
25%     7.823826e+08            2023-07-07 13:50:00   
50%     8.086351e+08            2023-07-14 13:50:00   
75%     8.087473e+08            2023-07-22 14:20:00   
max     8.323115e+08            2023-07-31 14:50:00   
std     1.653247e+07                            NaN   

                 tier_trips_end_time              trip_duration  \
count                           2085                       2085   
mean   2023-07-15 15:41:39.568345088  0 days 00:14:35.395683453   
min              2023-07-01 12:25:00            0 days 00:05:00   
25%              2023-07-07 14:00:00            0 days 00:10:00   
50%              2023-07-14 14:05:00            0 days 00:10:00   
75%              2023-07-22 14:35:00            0 days 00:15:00   
max              2023-07-31 16:40:00            0 days 01:55:00   
std                              NaN  0 days 00:10:02.262129818   

       trip_distance_kilometers  trip_distance_meters  start_stop_id  \
count               2085.000000           2085.000000    1562.000000   
mean                   1.824715           1824.715173    1317.564661   
min                    0.102492            102.492070      43.000000   
25%                    0.781769            781.769071     693.000000   
50%                    1.383804           1383.803759    1115.000000   
75%                    2.347804           2347.804392    1290.000000   
max                   13.583168          13583.167599    9703.000000   
std                    1.597460           1597.459730    1370.225745   

       end_stop_id  trip_duration_seconds  
count  1104.000000            2085.000000  
mean   1422.985507             875.395683  
min      43.000000             300.000000  
25%    1102.000000             600.000000  
50%    1144.000000             600.000000  
75%    1291.250000             900.000000  
max    9780.000000            6900.000000  
std    1478.713545             602.262130

In [154]:
get_stats(lunchtime_nan_delay_tier, ['trip_duration_seconds', 'trip_distance_kilometers'])

column                                     trip_duration_seconds  \
rows                                                        2085   
sum                                                    1825200.0   
mean                                                  875.395683   
median                                                     600.0   
mode           0    600.0
Name: trip_duration_seconds, dtype:...   
max                                                       6900.0   
min                                                        300.0   
std_dev                                                602.26213   
variance                                           362719.673014   
skewness                                                3.657718   
kurtosis                                               21.917736   
percentile_25                                              600.0   
percentile_75                                              900.0   
iqr                                                        300.0   
range                                                     6600.0   
cv                                                      0.687988   
qd                                                           0.2   
cs                                                      0.006073   
ck                                                      0.036392   
cvs                                                     0.006073   
cvk                                                     0.036392   
cvcs                                                    0.006073   
cvck                                                    0.036392   
cvcv                                                    0.687988   
cvqd                                                         0.2   
cvr                                                     7.539448   
cvm                                                          1.0   
cvmed                                                   0.685404   
cvmode         0    0.685404
Name: trip_duration_seconds, dty...   

column                                  trip_distance_kilometers  
rows                                                        2085  
sum                                                  3804.531136  
mean                                                    1.824715  
median                                                  1.383804  
mode           0        0.102492
1        0.102924
2        0...  
max                                                    13.583168  
min                                                     0.102492  
std_dev                                                  1.59746  
variance                                                2.551878  
skewness                                                2.310805  
kurtosis                                                8.184748  
percentile_25                                           0.781769  
percentile_75                                           2.347804  
iqr                                                     1.566035  
range                                                  13.480676  
cv                                                      0.875457  
qd                                                      0.500399  
cs                                                       1.44655  
ck                                                      5.123602  
cvs                                                      1.44655  
cvk                                                     5.123602  
cvcs                                                     1.44655  
cvck                                                    5.123602  
cvcv                                                    0.875457  
cvqd                                                    0.500399  
cvr                                                     7.387825  
cvm                                                          1.0  
cvmed                                                   0.758367  
cvmode         0

In [155]:
# get entries where trips start and end at station
lunchtime_nan_delay_tier_station_station = lunchtime_nan_delay_tier[lunchtime_nan_delay_tier['end_stop_id'].notna() & lunchtime_nan_delay_tier['start_stop_id'].notna()]
lunchtime_nan_delay_tier_station_station

tier_trips_id tier_trips_start_time tier_trips_end_time vehicle type  \
3064561      782314064   2023-07-01 12:15:00 2023-07-01 12:25:00    e-scooter   
3238616      782417783   2023-07-01 12:20:00 2023-07-01 12:30:00    e-scooter   
3278736      782454329   2023-07-01 12:20:00 2023-07-01 12:35:00    e-scooter   
3226921      782407118   2023-07-01 12:20:00 2023-07-01 12:30:00    e-scooter   
3082973      782320108   2023-07-01 12:20:00 2023-07-01 12:25:00    e-scooter   
...                ...                   ...                 ...          ...   
3523189      832301874   2023-07-31 14:25:00 2023-07-31 14:40:00    e-scooter   
3508084      832287375   2023-07-31 14:30:00 2023-07-31 14:45:00    e-scooter   
3491611      832271568   2023-07-31 14:30:00 2023-07-31 14:45:00    e-scooter   
3482733      832263064   2023-07-31 14:35:00 2023-07-31 14:40:00    e-scooter   
3419833      832202667   2023-07-31 14:50:00 2023-07-31 14:55:00    e-scooter   

          trip_duration  trip_distance_kilometers  trip_distance_meters  \
3064561 0 days 00:10:00                  2.363972           2363.972459   
3238616 0 days 00:10:00                  0.864217            864.217127   
3278736 0 days 00:15:00                  2.391213           2391.212980   
3226921 0 days 00:10:00                  0.980556            980.556253   
3082973 0 days 00:05:00                  0.330897            330.896717   
...                 ...                       ...                   ...   
3523189 0 days 00:15:00                  1.388031           1388.030832   
3508084 0 days 00:15:00                  2.525054           2525.054040   
3491611 0 days 00:15:00                  2.123778           2123.777937   
3482733 0 days 00:05:00                  0.574873            574.872838   
3419833 0 days 00:05:00                  1.108613           1108.612542   

         start_stop_id                            start_stop_name  \
3064561         2667.0  Bonn Brüdergasse/Bertha-Von-Suttner-Platz   
3238616          687.0                                   Bonn Hbf   
3278736         1500.0                 Bonn Konrad-Adenauer-Platz   
3226921         1240.0                   Bonn Poppelsdorfer Platz   
3082973         1102.0                         Bonn Friedensplatz   
...                ...                                        ...   
3523189          687.0                                   Bonn Hbf   
3508084         1143.0                   Bonn Poppelsdorfer Allee   
3491611         1525.0                         Bonn Geislar Mitte   
3482733         1162.0                              Bonn Rosental   
3419833          687.0                                   Bonn Hbf   

                                         start_buffer_zone  end_stop_id  \
3064561  801621     POLYGON ((7.157885983913106 50.7227...       1504.0   
3238616  801621     POLYGON ((7.157885983913106 50.7227...       1115.0   
3278736  801621     POLYGON ((7.157885983913106 50.7227...       1586.0   
3226921  801621     POLYGON ((7.157885983913106 50.7227...       1242.0   
3082973  801621     POLYGON ((7.157885983913106 50.7227...       1104.0   
...                                                    ...          ...   
3523189  801621     POLYGON ((7.157885983913106 50.7227...       1136.0   
3508084  801621     POLYGON ((7.157885983913106 50.7227...       1620.0   
3491611  801621     POLYGON ((7.157885983913106 50.7227...       1513.0   
3482733  801621     POLYGON ((7.157885983913106 50.7227...       1111.0   
3419833  801621     POLYGON ((7.157885983913106 50.7227...       1140.0   

                                     end_stop_name  \
3064561                              Bonn Beuel Bf   
3238616  Bonn Bertha-Von-Suttner-Pl./Beethovenhaus   
3278736                             Bonn Limperich   
3226921                         Bonn Friedrichsruh   
3082973                             Bonn Stadthaus   
...                                            ...   
3523189                    

In [156]:
lunchtime_nan_delay_tier_station_station.describe()

tier_trips_id          tier_trips_start_time  \
count   9.320000e+02                            932   
mean    7.976262e+08  2023-07-15 07:09:30.064377856   
min     7.822648e+08            2023-07-01 12:15:00   
25%     7.823747e+08            2023-07-07 13:15:00   
50%     8.086214e+08            2023-07-13 14:42:30   
75%     8.087349e+08            2023-07-22 13:46:15   
max     8.323082e+08            2023-07-31 14:50:00   
std     1.628184e+07                            NaN   

                 tier_trips_end_time              trip_duration  \
count                            932                        932   
mean   2023-07-15 07:22:28.390557952  0 days 00:12:58.326180257   
min              2023-07-01 12:25:00            0 days 00:05:00   
25%              2023-07-07 13:25:00            0 days 00:10:00   
50%              2023-07-13 14:52:30            0 days 00:10:00   
75%              2023-07-22 14:00:00            0 days 00:15:00   
max              2023-07-31 15:05:00            0 days 01:35:00   
std                              NaN  0 days 00:08:23.715719573   

       trip_distance_kilometers  trip_distance_meters  start_stop_id  \
count                932.000000            932.000000     932.000000   
mean                   1.489938           1489.938190    1398.065451   
min                    0.102492            102.492070      43.000000   
25%                    0.706212            706.211776    1102.000000   
50%                    1.246288           1246.287767    1115.000000   
75%                    1.919354           1919.354101    1240.000000   
max                   13.583168          13583.167599    9703.000000   
std                    1.229942           1229.942344    1494.964876   

       end_stop_id  trip_duration_seconds  
count   932.000000              932.00000  
mean   1418.496781              778.32618  
min      43.000000              300.00000  
25%    1102.000000              600.00000  
50%    1150.000000              600.00000  
75%    1291.000000              900.00000  
max    9780.000000             5700.00000  
std    1417.745432              503.71572

In [157]:
# get statistics for the tier trips that start and end at a station
get_stats(lunchtime_nan_delay_tier_station_station, ['trip_duration_seconds', 'trip_distance_kilometers'])

column                                     trip_duration_seconds  \
rows                                                         932   
sum                                                     725400.0   
mean                                                   778.32618   
median                                                     600.0   
mode           0    600.0
Name: trip_duration_seconds, dtype:...   
max                                                       5700.0   
min                                                        300.0   
std_dev                                                503.71572   
variance                                           253729.526145   
skewness                                                4.110424   
kurtosis                                               28.756584   
percentile_25                                              600.0   
percentile_75                                              900.0   
iqr                                                        300.0   
range                                                     5400.0   
cv                                                      0.647178   
qd                                                           0.2   
cs                                                       0.00816   
ck                                                      0.057089   
cvs                                                      0.00816   
cvk                                                     0.057089   
cvcs                                                     0.00816   
cvck                                                    0.057089   
cvcv                                                    0.647178   
cvqd                                                         0.2   
cvr                                                     6.937965   
cvm                                                          1.0   
cvmed                                                   0.770885   
cvmode         0    0.770885
Name: trip_duration_seconds, dty...   

column                                  trip_distance_kilometers  
rows                                                         932  
sum                                                  1388.622393  
mean                                                    1.489938  
median                                                  1.246288  
mode           0       0.102492
1       0.102924
2       0.10...  
max                                                    13.583168  
min                                                     0.102492  
std_dev                                                 1.229942  
variance                                                1.512758  
skewness                                                 3.21432  
kurtosis                                               22.028084  
percentile_25                                           0.706212  
percentile_75                                           1.919354  
iqr                                                     1.213142  
range                                                  13.480676  
cv                                                      0.825499  
qd                                                       0.46205  
cs                                                      2.613391  
ck                                                     17.909851  
cvs                                                     2.613391  
cvk                                                    17.909851  
cvcs                                                    2.613391  
cvck                                                   17.909851  
cvcv                                                    0.825499  
cvqd                                                     0.46205  
cvr                                                     9.047809  
cvm                                                          1.0  
cvmed                                                   0.836469  
cvmode         0

In [158]:
lunchtime_nan_delay_next = check_micromobility_datasets('next', lunchtime_nan_delay)

In [159]:
lunchtime_nan_delay_next.describe()

nextbike_trips_id      nextbike_trips_start_time  \
count       5.457000e+03                           5457   
mean        3.794177e+07  2023-07-15 11:29:19.175371264   
min         3.771653e+07            2023-07-01 12:01:00   
25%         3.783141e+07            2023-07-07 13:11:00   
50%         3.794545e+07            2023-07-14 13:36:00   
75%         3.805123e+07            2023-07-22 14:11:00   
max         3.817171e+07            2023-07-31 15:01:00   
std         1.276978e+05                            NaN   

             nextbike_trips_end_time              trip_duration  \
count                           5457                       5457   
mean   2023-07-15 11:43:53.007146752  0 days 00:14:33.831775700   
min              2023-07-01 12:16:00            0 days 00:05:00   
25%              2023-07-07 13:26:00            0 days 00:10:00   
50%              2023-07-14 13:46:00            0 days 00:10:00   
75%              2023-07-22 14:26:00            0 days 00:15:00   
max              2023-07-31 15:21:00            0 days 02:00:00   
std                              NaN  0 days 00:10:19.298507224   

       trip_distance_kilometers  trip_distance_meters  start_stop_id  \
count               5457.000000           5457.000000    4316.000000   
mean                   1.621107           1621.106517    1153.697637   
min                    0.100321            100.320557      43.000000   
25%                    0.726545            726.544504     687.000000   
50%                    1.243446           1243.445910    1115.000000   
75%                    2.065264           2065.264184    1221.000000   
max                   13.602096          13602.096364    9780.000000   
std                    1.388334           1388.333563    1017.931912   

       end_stop_id  trip_duration_seconds  
count  3179.000000            5457.000000  
mean   1232.381252             873.831776  
min      43.000000             300.000000  
25%     691.500000             600.000000  
50%    1136.000000             600.000000  
75%    1221.000000             900.000000  
max    9780.000000            7200.000000  
std    1151.376333             619.298507

In [160]:
get_stats(lunchtime_nan_delay_next, ['trip_duration_seconds', 'trip_distance_kilometers'])

column                                     trip_duration_seconds  \
rows                                                        5457   
sum                                                    4768500.0   
mean                                                  873.831776   
median                                                     600.0   
mode           0    600.0
Name: trip_duration_seconds, dtype:...   
max                                                       7200.0   
min                                                        300.0   
std_dev                                               619.298507   
variance                                            383530.64105   
skewness                                                4.358192   
kurtosis                                               30.271472   
percentile_25                                              600.0   
percentile_75                                              900.0   
iqr                                                        300.0   
range                                                     6900.0   
cv                                                      0.708716   
qd                                                           0.2   
cs                                                      0.007037   
ck                                                       0.04888   
cvs                                                     0.007037   
cvk                                                      0.04888   
cvcs                                                    0.007037   
cvck                                                     0.04888   
cvcv                                                    0.708716   
cvqd                                                         0.2   
cvr                                                     7.896257   
cvm                                                          1.0   
cvmed                                                   0.686631   
cvmode         0    0.686631
Name: trip_duration_seconds, dty...   

column                                  trip_distance_kilometers  
rows                                                        5457  
sum                                                  8846.378263  
mean                                                    1.621107  
median                                                  1.243446  
mode           0    0.376674
1    0.870199
Name: trip_distanc...  
max                                                    13.602096  
min                                                     0.100321  
std_dev                                                 1.388334  
variance                                                 1.92747  
skewness                                                2.416626  
kurtosis                                                9.073573  
percentile_25                                           0.726545  
percentile_75                                           2.065264  
iqr                                                      1.33872  
range                                                  13.501776  
cv                                                      0.856411  
qd                                                      0.479517  
cs                                                      1.740667  
ck                                                      6.535586  
cvs                                                     1.740667  
cvk                                                     6.535586  
cvcs                                                    1.740667  
cvck                                                    6.535586  
cvcv                                                    0.856411  
cvqd                                                    0.479517  
cvr                                                     8.328741  
cvm                                                          1.0  
cvmed                                                   0.767035  
cvmode         0

In [161]:
# get entries where trips start and end at station
lunchtime_nan_delay_next_station_station = lunchtime_nan_delay_next[lunchtime_nan_delay_next['end_stop_id'].notna() & lunchtime_nan_delay_next['start_stop_id'].notna()]
lunchtime_nan_delay_next_station_station

nextbike_trips_id nextbike_trips_start_time nextbike_trips_end_time  \
1524518           38077625       2023-07-01 12:06:00     2023-07-01 12:26:00   
1288123           37837777       2023-07-01 12:06:00     2023-07-01 12:21:00   
1480170           38042641       2023-07-01 12:06:00     2023-07-01 12:16:00   
1585494           38127994       2023-07-01 12:11:00     2023-07-01 12:21:00   
1383789           37945449       2023-07-01 12:16:00     2023-07-01 12:26:00   
...                    ...                       ...                     ...   
1552117           38098935       2023-07-31 14:51:00     2023-07-31 15:06:00   
1301122           37878906       2023-07-31 14:56:00     2023-07-31 15:06:00   
1467817           37975497       2023-07-31 14:56:00     2023-07-31 15:06:00   
1533238           38084253       2023-07-31 14:56:00     2023-07-31 15:16:00   
1506797           38063030       2023-07-31 15:01:00     2023-07-31 15:16:00   

         nextbike_trips_start_at_station  nextbike_trips_end_at_station  \
1524518                             True                          False   
1288123                             True                          False   
1480170                            False                          False   
1585494                            False                          False   
1383789                            False                          False   
...                                  ...                            ...   
1552117                            False                          False   
1301122                            False                          False   
1467817                            False                          False   
1533238                            False                          False   
1506797                            False                          False   

        vehicle type   trip_duration  trip_distance_kilometers  \
1524518         bike 0 days 00:20:00                  1.235203   
1288123         bike 0 days 00:15:00                  3.492510   
1480170         bike 0 days 00:10:00                  0.768149   
1585494         bike 0 days 00:10:00                  1.398754   
1383789         bike 0 days 00:10:00                  0.415754   
...              ...             ...                       ...   
1552117         bike 0 days 00:15:00                  1.331125   
1301122         bike 0 days 00:10:00                  1.354012   
1467817         bike 0 days 00:10:00                  0.443949   
1533238         bike 0 days 00:20:00                  1.684933   
1506797         bike 0 days 00:15:00                  3.304795   

         trip_distance_meters  \
1524518           1235.202730   
1288123           3492.510346   
1480170            768.148794   
1585494           1398.753812   
1383789            415.754205   
...                       ...   
1552117           1331.125192   
1301122           1354.011648   
1467817            443.949088   
1533238           1684.933448   
1506797           3304.795051   

                                            start_location  \
1524518  b'\x01\x01\x00\x00\x00t\xef\xe1\x92\xe3\x9e\x1...   
1288123  b'\x01\x01\x00\x00\x007m\xc6i\x88z\x1c@\xb0\xf...   
1480170  b'\x01\x01\x00\x00\x00\xdcGnM\xbam\x1c@\xcc(\x...   
1585494  b'\x01\x01\x00\x00\x00\xa9\xa5\xb9\x15\xc2j\x1...   
1383789  b'\x01\x01\x00\x00\x00\x14\xcb-\xad\x86d\x1c@\...   
...                                                    ...   
1552117  b'\x01\x01\x00\x00\x00\x85\xee\x928+b\x1c@\x99...   
1301122  b'\x01\x01\x00\x00\x00\xa1\x9f\xa9\xd7-b\x1c@\...   
1467817  b'\x01\x01\x00\x00\x00)\x94\x85\xaf\xafe\x1c@h...   
1533238  b'\x01\x01\x00\x00\x00\xccD\x11R\xb7c\x1c@>w\x...   
1506797  b'\x01\x01\x00\x00\x00\xdf\xf8\xda3Kb\x1c@\x9e...   

                                              end_location  start_stop_id  \
1524518  b'\x01\x01\x00\x00\x00\x84\xd5X\xc2\xda\xa8\x1...         1584.0   
1288123  b'\x01\x01\x00\x00\x00\x92Z(\x99\x9cZ\x1c@QO\x...

In [162]:
lunchtime_nan_delay_next_station_station.describe()

nextbike_trips_id      nextbike_trips_start_time  \
count       2.702000e+03                           2702   
mean        3.794411e+07  2023-07-15 09:55:08.593634304   
min         3.771653e+07            2023-07-01 12:06:00   
25%         3.783689e+07            2023-07-07 13:46:00   
50%         3.794777e+07            2023-07-14 13:06:00   
75%         3.804904e+07            2023-07-22 13:21:00   
max         3.817160e+07            2023-07-31 15:01:00   
std         1.252168e+05                            NaN   

             nextbike_trips_end_time              trip_duration  \
count                           2702                       2702   
mean   2023-07-15 10:08:24.781643264  0 days 00:13:16.188008882   
min              2023-07-01 12:16:00            0 days 00:05:00   
25%              2023-07-07 13:56:00            0 days 00:10:00   
50%              2023-07-14 13:16:00            0 days 00:10:00   
75%              2023-07-22 13:43:30            0 days 00:15:00   
max              2023-07-31 15:16:00            0 days 02:00:00   
std                              NaN  0 days 00:09:01.854541827   

       trip_distance_kilometers  trip_distance_meters  start_stop_id  \
count               2702.000000           2702.000000    2702.000000   
mean                   1.352163           1352.163396    1175.136936   
min                    0.100321            100.320557      43.000000   
25%                    0.668600            668.600120     687.000000   
50%                    1.115542           1115.542251    1115.000000   
75%                    1.701694           1701.693547    1221.000000   
max                    8.605918           8605.918179    9780.000000   
std                    1.054423           1054.422779    1030.691051   

       end_stop_id  trip_duration_seconds  
count  2702.000000            2702.000000  
mean   1265.439674             796.188009  
min      43.000000             300.000000  
25%     699.000000             600.000000  
50%    1140.000000             600.000000  
75%    1221.000000             900.000000  
max    9780.000000            7200.000000  
std    1186.203438             541.854542

In [163]:
# get statistics for the tier trips that start and end at a station
get_stats(lunchtime_nan_delay_next_station_station, ['trip_duration_seconds', 'trip_distance_kilometers'])

column                                     trip_duration_seconds  \
rows                                                        2702   
sum                                                    2151300.0   
mean                                                  796.188009   
median                                                     600.0   
mode           0    600.0
Name: trip_duration_seconds, dtype:...   
max                                                       7200.0   
min                                                        300.0   
std_dev                                               541.854542   
variance                                           293606.344499   
skewness                                                5.159073   
kurtosis                                               44.744889   
percentile_25                                              600.0   
percentile_75                                              900.0   
iqr                                                        300.0   
range                                                     6900.0   
cv                                                      0.680561   
qd                                                           0.2   
cs                                                      0.009521   
ck                                                      0.082577   
cvs                                                     0.009521   
cvk                                                     0.082577   
cvcs                                                    0.009521   
cvck                                                    0.082577   
cvcv                                                    0.680561   
cvqd                                                         0.2   
cvr                                                     8.666295   
cvm                                                          1.0   
cvmed                                                   0.753591   
cvmode         0    0.753591
Name: trip_duration_seconds, dty...   

column                                  trip_distance_kilometers  
rows                                                        2702  
sum                                                  3653.545497  
mean                                                    1.352163  
median                                                  1.115542  
mode           0    0.222838
Name: trip_distance_kilometers, ...  
max                                                     8.605918  
min                                                     0.100321  
std_dev                                                 1.054423  
variance                                                1.111807  
skewness                                                2.005577  
kurtosis                                                6.069395  
percentile_25                                             0.6686  
percentile_75                                           1.701694  
iqr                                                     1.033093  
range                                                   8.505598  
cv                                                      0.779804  
qd                                                       0.43585  
cs                                                      1.902062  
ck                                                      5.756131  
cvs                                                     1.902062  
cvk                                                     5.756131  
cvcs                                                    1.902062  
cvck                                                    5.756131  
cvcv                                                    0.779804  
cvqd                                                     0.43585  
cvr                                                     6.290362  
cvm                                                          1.0  
cvmed                                                   0.825006  
cvmode         0

In [164]:
lunchtime_delay.describe()

route_id      agency_id     route_type     service_id  \
count  167732.000000  167732.000000  167732.000000  167732.000000   
mean      565.041435       6.007071       2.756826    2958.531109   
min        60.000000       6.000000       0.000000      43.000000   
25%       602.000000       6.000000       3.000000      64.000000   
50%       607.000000       6.000000       3.000000      64.000000   
75%       611.000000       6.000000       3.000000     130.000000   
max       843.000000      12.000000       3.000000   27690.000000   
std       151.841881       0.200333       0.818774    8288.605530   

        direction_id      shape_id        stop_id  \
count  167732.000000  167732.00000  167732.000000   
mean        0.517814    3582.13797    2303.104035   
min         0.000000       6.00000      43.000000   
25%         0.000000    1915.00000    1213.000000   
50%         1.000000    2717.00000    1441.000000   
75%         1.000000    5633.00000    1673.000000   
max         1.000000   10365.00000    9780.000000   
std         0.499684    2819.36219    2398.882564   

                 actual_arrival_time          actual_departure_time  \
count                         162984                         167732   
mean   2023-07-16 10:51:48.361649152  2023-07-16 11:31:20.446515968   
min              2023-07-01 12:00:00            2023-07-01 12:00:15   
25%              2023-07-08 14:29:15            2023-07-08 14:29:30   
50%              2023-07-15 14:14:00            2023-07-15 14:25:15   
75%              2023-07-24 12:28:00            2023-07-24 12:37:45   
max              2023-07-31 15:11:45            2023-07-31 15:12:00   
std                              NaN                            NaN   

       vrs_timestamp  ...  departure_delay_float actual_arrival_time_float  \
count  167732.000000  ...          167732.000000             167732.000000   
mean   127015.706848  ...               0.690005             129072.150186   
min    100304.000000  ...               0.166667                  0.000000   
25%    112307.000000  ...               0.250000             124030.000000   
50%    121305.000000  ...               0.500000             132615.000000   
75%    130306.000000  ...               0.750000             141115.000000   
max    220309.000000  ...             112.500000             151145.000000   
std     28066.103678  ...               2.154846              23501.402098   

      actual_departure_time_float arrival_delay_span    weather_int  \
count               167732.000000           167732.0  167732.000000   
mean                132878.455244                0.0       0.166778   
min                 120010.000000                0.0       0.000000   
25%                 124445.000000                0.0       0.000000   
50%                 132920.000000                0.0       0.000000   
75%                 141245.000000                0.0       0.000000   
max                 151200.000000                0.0       2.000000   
std                   8303.283312                0.0       0.446188   

       time_span_int_arrival        weekend  time_span_int  delay_category  \
count          167732.000000  167732.000000  167732.000000   167732.000000   
mean                2.915681       0.748229       3.001145        0.635979   
min                 0.000000       0.000000       3.000000       -1.000000   
25%                 3.000000       0.000000       3.000000        0.000000   
50%                 3.000000       0.000000       3.000000        1.000000   
75%                 3.000000       2.000000       3.000000        1.000000   
max                 4.000000       3.000000       4.000000        1.000000   
std                 0.498458       1.038669       0.033814        0.536773   

       cancelled_trip  
count        167732.0  
mean              0.0  
min               0.0  
25%               0.0  
50%               0.0  
75%               0.0  
max               0.0  
std               0.0  

[8 rows x

In [165]:
lunchtime_no_delay.describe()

route_id      agency_id     route_type     service_id  \
count  105922.000000  105922.000000  105922.000000  105922.000000   
mean      562.643304       7.058137       2.604530    5623.194237   
min        16.000000       1.000000       0.000000      43.000000   
25%       551.000000       6.000000       3.000000      64.000000   
50%       607.000000       6.000000       3.000000      64.000000   
75%       630.000000       8.000000       3.000000     151.000000   
max       884.000000      12.000000       3.000000   29144.000000   
std       218.152984       2.160417       1.014901   10963.061893   

        direction_id       shape_id        stop_id  \
count  105922.000000  105922.000000  105922.000000   
mean        0.504267    4252.524594    2182.383877   
min         0.000000       6.000000      43.000000   
25%         0.000000    2021.000000    1175.000000   
50%         1.000000    3858.000000    1406.000000   
75%         1.000000    6377.000000    1710.000000   
max         1.000000   10365.000000    9780.000000   
std         0.499984    2852.621260    2323.349001   

                 actual_arrival_time          actual_departure_time  \
count                          76034                         105922   
mean   2023-07-16 11:05:08.110516224  2023-07-16 11:41:05.587177216   
min              2023-07-01 11:59:00            2023-07-01 12:00:00   
25%              2023-07-08 14:14:45            2023-07-08 14:19:00   
50%              2023-07-15 14:22:45            2023-07-15 14:39:00   
75%    2023-07-24 12:40:43.750000128            2023-07-24 12:50:00   
max              2023-07-31 14:58:45            2023-07-31 14:59:15   
std                              NaN                            NaN   

       vrs_timestamp  ...  departure_delay_float actual_arrival_time_float  \
count  105922.000000  ...          105922.000000             105922.000000   
mean   126867.289742  ...               0.041834              95251.241055   
min    100304.000000  ...               0.000000                  0.000000   
25%    112804.000000  ...               0.000000                  0.000000   
50%    121307.000000  ...               0.000000             125345.000000   
75%    130307.000000  ...               0.000000             135400.000000   
max    220309.000000  ...             111.500000             150200.000000   
std     27674.642780  ...               0.636639              60127.535373   

      actual_departure_time_float arrival_delay_span    weather_int  \
count               105922.000000           105922.0  105922.000000   
mean                132896.279196                0.0       0.172872   
min                 115615.000000                0.0       0.000000   
25%                 124500.000000                0.0       0.000000   
50%                 132900.000000                0.0       0.000000   
75%                 141300.000000                0.0       0.000000   
max                 151100.000000                0.0       2.000000   
std                   8264.342416                0.0       0.455117   

       time_span_int_arrival        weekend  time_span_int  delay_category  \
count          105922.000000  105922.000000  105922.000000   105922.000000   
mean                2.150233       0.738685       3.000245       -0.274976   
min                 0.000000       0.000000       2.000000       -1.000000   
25%                 0.000000       0.000000       3.000000       -1.000000   
50%                 3.000000       0.000000       3.000000        0.000000   
75%                 3.000000       2.000000       3.000000        0.000000   
max                 4.000000       3.000000       4.000000        1.000000   
std                 1.349340       1.025455       0.021725        0.462336   

       cancelled_trip  
count        105922.0  
mean              0.0  
min               0.0  
25%               0.0  
50%               0.0  
75%               0.0  
max               0.0  
std               0.0  



In [166]:
lunchtime_nan_delay.describe()

route_id      agency_id     route_type     service_id  \
count  186150.000000  186150.000000  186150.000000  186150.000000   
mean      554.988848       6.333844       2.671104    4125.233822   
min        16.000000       1.000000       0.000000      43.000000   
25%       601.000000       6.000000       3.000000      64.000000   
50%       607.000000       6.000000       3.000000      64.000000   
75%       613.000000       6.000000       3.000000     130.000000   
max       884.000000      12.000000       3.000000   29145.000000   
std       183.126199       1.263509       0.937294    9611.833525   

        direction_id       shape_id        stop_id actual_arrival_time  \
count  186150.000000  186150.000000  186150.000000                   0   
mean        0.491829    4084.022944    2252.653398                 NaT   
min         0.000000       6.000000      43.000000                 NaT   
25%         0.000000    1975.000000    1221.000000                 NaT   
50%         0.000000    2952.000000    1456.000000                 NaT   
75%         1.000000    6327.000000    1685.000000                 NaT   
max         1.000000   10365.000000    9780.000000                 NaT   
std         0.499935    2925.498064    2342.340408                 NaN   

      actual_departure_time  vrs_timestamp  ...  departure_delay_float  \
count                     0  186150.000000  ...                    0.0   
mean                    NaT  121908.225689  ...                    NaN   
min                     NaT   72804.000000  ...                    NaN   
25%                     NaT  112804.000000  ...                    NaN   
50%                     NaT  121305.000000  ...                    NaN   
75%                     NaT  130305.000000  ...                    NaN   
max                     NaT  220309.000000  ...                    NaN   
std                     NaN   17256.496969  ...                    NaN   

      actual_arrival_time_float actual_departure_time_float  \
count                  186150.0                    186150.0   
mean                        0.0                         0.0   
min                         0.0                         0.0   
25%                         0.0                         0.0   
50%                         0.0                         0.0   
75%                         0.0                         0.0   
max                         0.0                         0.0   
std                         0.0                         0.0   

      arrival_delay_span    weather_int  time_span_int_arrival        weekend  \
count           186150.0  186150.000000               186150.0  186150.000000   
mean                 0.0       0.202364                    0.0       0.707268   
min                  0.0       0.000000                    0.0       0.000000   
25%                  0.0       0.000000                    0.0       0.000000   
50%                  0.0       0.000000                    0.0       0.000000   
75%                  0.0       0.000000                    0.0       1.000000   
max                  0.0       2.000000                    0.0       3.000000   
std                  0.0       0.491831                    0.0       0.983494   

       time_span_int  delay_category  cancelled_trip  
count       186150.0        186150.0        186150.0  
mean             0.0            -1.0             1.0  
min              0.0            -1.0             1.0  
25%              0.0            -1.0             1.0  
50%              0.0            -1.0             1.0  
75%              0.0            -1.0             1.0  
max              0.0            -1.0             1.0  
std              0.0             0.0             0.0  

[8 rows x 38 columns]

#### Afternoon

In [167]:
afternoon_delay = delay[(delay['scheduled_arrival_time'].dt.hour > 14) & (delay['scheduled_arrival_time'].dt.hour < 17)]
afternoon_delay

route_id  agency_id route_short_name  route_type route_type_name  \
43972          65          6               65           0            Tram   
43978         602          6              602           3             Bus   
43980         630          6              630           3             Bus   
43981         611          6              611           3             Bus   
43985         632          6              632           3             Bus   
...           ...        ...              ...         ...             ...   
2533610       610          6              610           3             Bus   
2533611       605          6              605           3             Bus   
2533614        65          6               65           0            Tram   
2533616       611          6              611           3             Bus   
2533618       608          6              608           3             Bus   

                               agency_name  service_id  \
43972    SWB Stadtwerke Bonn Verkehrs GmbH       26814   
43978    SWB Stadtwerke Bonn Verkehrs GmbH         130   
43980    SWB Stadtwerke Bonn Verkehrs GmbH         130   
43981    SWB Stadtwerke Bonn Verkehrs GmbH         130   
43985    SWB Stadtwerke Bonn Verkehrs GmbH         130   
...                                    ...         ...   
2533610  SWB Stadtwerke Bonn Verkehrs GmbH          64   
2533611  SWB Stadtwerke Bonn Verkehrs GmbH          64   
2533614  SWB Stadtwerke Bonn Verkehrs GmbH       26825   
2533616  SWB Stadtwerke Bonn Verkehrs GmbH          64   
2533618  SWB Stadtwerke Bonn Verkehrs GmbH          64   

                                                   trip_id  \
43972    650718-65-006-1406.1.12:143400-24-178_32CE736F...   
43978    6020161-602-006-1307.2.22:142200-37-1_99507F62...   
43980    6300084-630-006-9478.2.22:143100-50-1_4290188D...   
43981    6110191-611-006-1723.2.21:140600-60-1_CC0FCA5F...   
43985    6320214-632-006-8832.2.23:145400-26-1_963E15FE...   
...                                                    ...   
2533610  6100106-610-006-1341.2.24:165200-53-1_7B648BAB...   
2533611  6050105-605-006-1341.2.24:164600-40-1_07E67217...   
2533614  651118-65-006-1406.1.12:165400-24-179_A91BFD72...   
2533616  6110116-611-006-1338.2.21:162000-58-1_2B7A7D40...   
2533618  6080097-608-006-1374.2.21:164100-46-1_1C8573C9...   

                       trip_headsign  direction_id  ...  delay_span  \
43972    Oberkassel Süd/Römlinghoven             1  ...         0-5   
43978             Agnetendorfer Str.             0  ...         0-5   
43980                Uniklinikum Süd             1  ...         0-5   
43981           Lessenich Sportplatz             0  ...         0-5   
43985                Uniklinikum Süd             1  ...         0-5   
...                              ...           ...  ...         ...   
2533610                 Giselherstr.             1  ...         0-5   
2533611              Mondorfer Fähre             0  ...         0-5   
2533614  Oberkassel Süd/Römlinghoven             1  ...         0-5   
2533616                    Pappelweg             1  ...         0-5   
2533618                      Gielgen             0  ...         0-5   

         arrival_delay_span weather_int time_span_arrival  \
43972                     0           0                 0   
43978                     0           0         afternoon   
43980                     0           0         afternoon   
43981                     0           0         afternoon   
43985                     0           0         afternoon   
...                     ...         ...               ...   
2533610                   0           1         afternoon   
2533611                   0           1         afternoon   
2533614                   0           1         afternoon   
2533616                   0           1         afternoon   
2533618                   0           1         afternoon   

         time_span_int_arrival  weekend  time_span time_

In [168]:
get_stats(afternoon_delay, ['tier_trips_count', 'tier_trips_end_at_station_count', 'nextbike_trips_count', 'nextbike_trips_end_at_station_count', 'current_temp', 'current_precipitation_volume'])

/tmp/ipykernel_2575952/41814695.py:51: RuntimeWarning: invalid value encountered in scalar divide
  qd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:55: RuntimeWarning: invalid value encountered in scalar divide
  cvqd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:51: RuntimeWarning: invalid value encountered in scalar divide
  qd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:55: RuntimeWarning: invalid value encountered in scalar divide
  cvqd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:51: RuntimeWarning: invalid value encountered in scalar divide
  qd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:55: RuntimeWarning: invalid value encountered in scalar divide
  cvqd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:51: RuntimeWarning: invalid value encountered in scalar divide
  qd = iqr / (percentile_75 + percenti

column                                        tier_trips_count  \
rows                                                    110777   
sum                                                       2158   
mean                                                  0.019481   
median                                                     0.0   
mode               0    0
Name: tier_trips_count, dtype: int64   
max                                                          5   
min                                                          0   
std_dev                                               0.152077   
variance                                              0.023127   
skewness                                              9.264322   
kurtosis                                            112.056299   
percentile_25                                              0.0   
percentile_75                                              0.0   
iqr                                                        0.0   
range                                                        5   
cv                                                    7.806594   
qd                                                         NaN   
cs                                                   60.918644   
ck                                                  736.839444   
cvs                                                  60.918644   
cvk                                                 736.839444   
cvcs                                                 60.918644   
cvck                                                736.839444   
cvcv                                                  7.806594   
cvqd                                                       NaN   
cvr                                                 256.665894   
cvm                                                        1.0   
cvmed                                                      0.0   
cvmode         0    0.0
Name: tier_trips_count, dtype: float64   

column                           tier_trips_end_at_station_count  \
rows                                                      110777   
sum                                                         1779   
mean                                                    0.016059   
median                                                       0.0   
mode           0    0
Name: tier_trips_end_at_station_count, ...   
max                                                            4   
min                                                            0   
std_dev                                                 0.136514   
variance                                                0.018636   
skewness                                                9.918014   
kurtosis                                              125.883348   
percentile_25                                                0.0   
percentile_75                                                0.0   
iqr                                                          0.0   
range                                                          4   
cv                                                      8.500627   
qd                                                           NaN   
cs                                                     72.651975   
ck                                                     922.12753   
cvs                                                    72.651975   
cvk                                                    922.12753   
cvcs                                                   72.651975   
cvck                                                   922.12753   
cvcv                                                    8.500627   
cvqd                                                         NaN   
cvr                                                    249.07701   
cvm                                                          1.0   
cvmed                                                        0.0   
cvmode         0    0.0
Name: tier_trips_end_at

In [169]:
afternoon_delay_tier = check_micromobility_datasets('tier', afternoon_delay)

In [170]:
afternoon_delay_tier.describe()

tier_trips_id          tier_trips_start_time  \
count   1.485000e+03                           1485   
mean    7.990602e+08  2023-07-15 11:34:32.121211904   
min     7.822646e+08            2023-07-01 15:10:00   
25%     7.823827e+08            2023-07-07 16:00:00   
50%     8.086366e+08            2023-07-13 16:35:00   
75%     8.087478e+08            2023-07-22 15:45:00   
max     8.323097e+08            2023-07-31 16:45:00   
std     1.670086e+07                            NaN   

                 tier_trips_end_time              trip_duration  \
count                           1485                       1485   
mean   2023-07-15 11:48:43.838384128  0 days 00:14:11.717171717   
min              2023-07-01 15:20:00            0 days 00:05:00   
25%              2023-07-07 16:15:00            0 days 00:10:00   
50%              2023-07-13 16:40:00            0 days 00:10:00   
75%              2023-07-22 16:00:00            0 days 00:15:00   
max              2023-07-31 17:00:00            0 days 01:45:00   
std                              NaN  0 days 00:09:56.783901488   

       trip_distance_kilometers  trip_distance_meters  start_stop_id  \
count               1485.000000           1485.000000    1051.000000   
mean                   1.708198           1708.197838    1460.949572   
min                    0.100973            100.972556     161.000000   
25%                    0.721766            721.766429    1102.000000   
50%                    1.289832           1289.832285    1140.000000   
75%                    2.249328           2249.327535    1268.000000   
max                    8.118360           8118.359836    9780.000000   
std                    1.403837           1403.837302    1522.855455   

       end_stop_id  trip_duration_seconds  
count   810.000000            1485.000000  
mean   1280.512346             851.717172  
min      43.000000             300.000000  
25%    1102.000000             600.000000  
50%    1140.000000             600.000000  
75%    1231.000000             900.000000  
max    9703.000000            6300.000000  
std    1149.003370             596.783901

In [171]:
get_stats(afternoon_delay_tier, ['trip_duration_seconds', 'trip_distance_kilometers'])

column                                     trip_duration_seconds  \
rows                                                        1485   
sum                                                    1264800.0   
mean                                                  851.717172   
median                                                     600.0   
mode           0    600.0
Name: trip_duration_seconds, dtype:...   
max                                                       6300.0   
min                                                        300.0   
std_dev                                               596.783901   
variance                                           356151.025076   
skewness                                                3.727001   
kurtosis                                               22.401885   
percentile_25                                              600.0   
percentile_75                                              900.0   
iqr                                                        300.0   
range                                                     6000.0   
cv                                                      0.700683   
qd                                                           0.2   
cs                                                      0.006245   
ck                                                      0.037538   
cvs                                                     0.006245   
cvk                                                     0.037538   
cvcs                                                    0.006245   
cvck                                                    0.037538   
cvcv                                                    0.700683   
cvqd                                                         0.2   
cvr                                                     7.044592   
cvm                                                          1.0   
cvmed                                                   0.704459   
cvmode         0    0.704459
Name: trip_duration_seconds, dty...   

column                                  trip_distance_kilometers  
rows                                                        1485  
sum                                                  2536.673789  
mean                                                    1.708198  
median                                                  1.289832  
mode           0       0.100973
1       0.100973
2       0.10...  
max                                                      8.11836  
min                                                     0.100973  
std_dev                                                 1.403837  
variance                                                1.970759  
skewness                                                1.594454  
kurtosis                                                2.808424  
percentile_25                                           0.721766  
percentile_75                                           2.249328  
iqr                                                     1.527561  
range                                                   8.017387  
cv                                                      0.821824  
qd                                                      0.514141  
cs                                                      1.135783  
ck                                                      2.000534  
cvs                                                     1.135783  
cvk                                                     2.000534  
cvcs                                                    1.135783  
cvck                                                    2.000534  
cvcv                                                    0.821824  
cvqd                                                    0.514141  
cvr                                                     4.693477  
cvm                                                          1.0  
cvmed                                                   0.755084  
cvmode         0

In [172]:
# get entries where trips start and end at station
afternoon_delay_tier_station_station = afternoon_delay_tier[afternoon_delay_tier['end_stop_id'].notna() & afternoon_delay_tier['start_stop_id'].notna()]
afternoon_delay_tier_station_station

tier_trips_id tier_trips_start_time tier_trips_end_time vehicle type  \
3202018      782383767   2023-07-01 15:10:00 2023-07-01 15:20:00    e-scooter   
3219195      782400097   2023-07-01 15:15:00 2023-07-01 15:45:00    e-scooter   
2951815      782279580   2023-07-01 15:10:00 2023-07-01 15:20:00    e-scooter   
3051714      782310016   2023-07-01 15:35:00 2023-07-01 15:45:00    e-scooter   
3005930      782296128   2023-07-01 15:50:00 2023-07-01 16:00:00    e-scooter   
...                ...                   ...                 ...          ...   
3370550      832155781   2023-07-31 16:10:00 2023-07-31 16:20:00    e-scooter   
3444519      832226390   2023-07-31 16:10:00 2023-07-31 16:25:00    e-scooter   
3520750      832299536   2023-07-31 16:20:00 2023-07-31 16:35:00    e-scooter   
3380897      832165359   2023-07-31 16:30:00 2023-07-31 16:35:00    e-scooter   
3406811      832190220   2023-07-31 16:45:00 2023-07-31 17:00:00    e-scooter   

          trip_duration  trip_distance_kilometers  trip_distance_meters  \
3202018 0 days 00:10:00                  0.514913            514.913225   
3219195 0 days 00:30:00                  4.263048           4263.048212   
2951815 0 days 00:10:00                  0.996590            996.590090   
3051714 0 days 00:10:00                  0.962415            962.414726   
3005930 0 days 00:10:00                  0.184171            184.170567   
...                 ...                       ...                   ...   
3370550 0 days 00:10:00                  0.344273            344.272909   
3444519 0 days 00:15:00                  2.137650           2137.649578   
3520750 0 days 00:15:00                  1.526621           1526.621152   
3380897 0 days 00:05:00                  0.265767            265.766999   
3406811 0 days 00:15:00                  3.037464           3037.463725   

         start_stop_id              start_stop_name  \
3202018         1110.0           Bonn Wilhelmsplatz   
3219195         1513.0        Bonn Rheindorfer Str.   
2951815         1411.0                Bonn Hoogland   
3051714         1411.0                Bonn Hoogland   
3005930         1110.0           Bonn Wilhelmsplatz   
...                ...                          ...   
3370550         1111.0  Bonn Beethovenhalle Und Swb   
3444519         1146.0                Bonn Bachstr.   
3520750         1223.0              Bonn Beringstr.   
3380897         1144.0           Bonn Beethovenstr.   
3406811         1221.0            Bonn Kaufmannstr.   

                                         start_buffer_zone  end_stop_id  \
3202018  801621     POLYGON ((7.157885983913106 50.7227...       1115.0   
3219195  801621     POLYGON ((7.157885983913106 50.7227...       1268.0   
2951815  801621     POLYGON ((7.157885983913106 50.7227...        695.0   
3051714  801621     POLYGON ((7.157885983913106 50.7227...        695.0   
3005930  801621     POLYGON ((7.157885983913106 50.7227...       1162.0   
...                                                    ...          ...   
3370550  801621     POLYGON ((7.157885983913106 50.7227...       1161.0   
3444519  801621     POLYGON ((7.157885983913106 50.7227...       1255.0   
3520750  801621     POLYGON ((7.157885983913106 50.7227...       1115.0   
3380897  801621     POLYGON ((7.157885983913106 50.7227...       1144.0   
3406811  801621     POLYGON ((7.157885983913106 50.7227...        684.0   

                                     end_stop_name  \
3202018  Bonn Bertha-Von-Suttner-Pl./Beethovenhaus   
3219195                              Bonn Rheinaue   
2951815                             Bonn Buschdorf   
3051714                             Bonn Buschdorf   
3005930                              Bonn Rosental   
...                                            ...   
3370550                          Bonn An Der Esche   
3444519                Bonn Graf-Stauffenberg-Str.   
3520750  Bonn Bertha-Von-Suttner-Pl./Beethovenhaus   
3380897                         B

In [173]:
afternoon_delay_tier_station_station.describe()

tier_trips_id          tier_trips_start_time  \
count   6.780000e+02                            678   
mean    7.990268e+08  2023-07-15 10:24:54.247787776   
min     7.822652e+08            2023-07-01 15:10:00   
25%     7.823788e+08            2023-07-07 16:31:15   
50%     8.086300e+08            2023-07-13 15:40:00   
75%     8.087423e+08            2023-07-22 15:50:00   
max     8.323097e+08            2023-07-31 16:45:00   
std     1.712122e+07                            NaN   

                 tier_trips_end_time              trip_duration  \
count                            678                        678   
mean   2023-07-15 10:38:00.530973440  0 days 00:13:06.283185840   
min              2023-07-01 15:20:00            0 days 00:05:00   
25%              2023-07-07 16:51:15            0 days 00:10:00   
50%              2023-07-13 15:52:30            0 days 00:10:00   
75%              2023-07-22 16:05:00            0 days 00:15:00   
max              2023-07-31 17:00:00            0 days 01:45:00   
std                              NaN  0 days 00:08:49.321119273   

       trip_distance_kilometers  trip_distance_meters  start_stop_id  \
count                678.000000            678.000000      678.00000   
mean                   1.408192           1408.192354     1481.29646   
min                    0.100973            100.972985      683.00000   
25%                    0.603560            603.559571     1102.25000   
50%                    1.041098           1041.098058     1141.50000   
75%                    1.937441           1937.441042     1240.00000   
max                    6.834481           6834.480582     9780.00000   
std                    1.140970           1140.969833     1547.87816   

       end_stop_id  trip_duration_seconds  
count   678.000000             678.000000  
mean   1311.606195             786.283186  
min      43.000000             300.000000  
25%    1102.000000             600.000000  
50%    1140.000000             600.000000  
75%    1223.000000             900.000000  
max    9703.000000            6300.000000  
std    1199.113732             529.321119

In [174]:
# get statistics for the tier trips that start and end at a station
get_stats(afternoon_delay_tier_station_station, ['trip_duration_seconds', 'trip_distance_kilometers'])

column                                     trip_duration_seconds  \
rows                                                         678   
sum                                                     533100.0   
mean                                                  786.283186   
median                                                     600.0   
mode           0    600.0
Name: trip_duration_seconds, dtype:...   
max                                                       6300.0   
min                                                        300.0   
std_dev                                               529.321119   
variance                                           280180.847309   
skewness                                                  3.8058   
kurtosis                                                24.89954   
percentile_25                                              600.0   
percentile_75                                              900.0   
iqr                                                        300.0   
range                                                     6000.0   
cv                                                      0.673194   
qd                                                           0.2   
cs                                                       0.00719   
ck                                                      0.047041   
cvs                                                      0.00719   
cvk                                                     0.047041   
cvcs                                                     0.00719   
cvck                                                    0.047041   
cvcv                                                    0.673194   
cvqd                                                         0.2   
cvr                                                     7.630838   
cvm                                                          1.0   
cvmed                                                   0.763084   
cvmode         0    0.763084
Name: trip_duration_seconds, dty...   

column                                  trip_distance_kilometers  
rows                                                         678  
sum                                                   954.754416  
mean                                                    1.408192  
median                                                  1.041098  
mode           0      0.100973
1      0.104994
2      0.10855...  
max                                                     6.834481  
min                                                     0.100973  
std_dev                                                  1.14097  
variance                                                1.301812  
skewness                                                1.619073  
kurtosis                                                3.071735  
percentile_25                                            0.60356  
percentile_75                                           1.937441  
iqr                                                     1.333881  
range                                                   6.733508  
cv                                                      0.810237  
qd                                                      0.524943  
cs                                                      1.419032  
ck                                                      2.692214  
cvs                                                     1.419032  
cvk                                                     2.692214  
cvcs                                                    1.419032  
cvck                                                    2.692214  
cvcv                                                    0.810237  
cvqd                                                    0.524943  
cvr                                                     4.781667  
cvm                                                          1.0  
cvmed                                                   0.739315  
cvmode         0

In [175]:
afternoon_delay_next = check_micromobility_datasets('next', afternoon_delay)

In [176]:
afternoon_delay_next.describe()

nextbike_trips_id      nextbike_trips_start_time  \
count       4.008000e+03                           4008   
mean        3.793764e+07  2023-07-15 22:53:54.251497216   
min         3.771653e+07            2023-07-01 15:01:00   
25%         3.782650e+07            2023-07-08 16:26:00   
50%         3.793689e+07            2023-07-14 16:56:00   
75%         3.804622e+07            2023-07-21 17:01:00   
max         3.817167e+07            2023-07-31 17:01:00   
std         1.279070e+05                            NaN   

             nextbike_trips_end_time              trip_duration  \
count                           4008                       4008   
mean   2023-07-15 23:09:20.598802176  0 days 00:15:26.347305389   
min              2023-07-01 15:11:00            0 days 00:05:00   
25%              2023-07-08 16:41:00            0 days 00:10:00   
50%              2023-07-14 17:13:30            0 days 00:15:00   
75%              2023-07-21 17:17:15            0 days 00:20:00   
max              2023-07-31 17:51:00            0 days 02:00:00   
std                              NaN  0 days 00:10:16.088623536   

       trip_distance_kilometers  trip_distance_meters  start_stop_id  \
count               4008.000000           4008.000000    2836.000000   
mean                   1.766768           1766.767631    1297.112130   
min                    0.100177            100.177408      43.000000   
25%                    0.789487            789.486830    1102.000000   
50%                    1.363061           1363.060627    1135.000000   
75%                    2.260204           2260.203848    1223.000000   
max                   11.879656          11879.655514    9780.000000   
std                    1.462954           1462.954055    1228.076836   

       end_stop_id  trip_duration_seconds  
count  2279.000000            4008.000000  
mean   1339.453269             926.347305  
min      43.000000             300.000000  
25%    1102.000000             600.000000  
50%    1150.000000             900.000000  
75%    1221.000000            1200.000000  
max    9703.000000            7200.000000  
std    1385.961585             616.088624

In [177]:
get_stats(afternoon_delay_next, ['trip_duration_seconds', 'trip_distance_kilometers'])

column                                     trip_duration_seconds  \
rows                                                        4008   
sum                                                    3712800.0   
mean                                                  926.347305   
median                                                     900.0   
mode           0    600.0
Name: trip_duration_seconds, dtype:...   
max                                                       7200.0   
min                                                        300.0   
std_dev                                               616.088624   
variance                                           379565.192052   
skewness                                                3.684906   
kurtosis                                               22.715705   
percentile_25                                              600.0   
percentile_75                                             1200.0   
iqr                                                        600.0   
range                                                     6900.0   
cv                                                      0.665073   
qd                                                      0.333333   
cs                                                      0.005981   
ck                                                      0.036871   
cvs                                                     0.005981   
cvk                                                     0.036871   
cvcs                                                    0.005981   
cvck                                                    0.036871   
cvcv                                                    0.665073   
cvqd                                                    0.333333   
cvr                                                      7.44861   
cvm                                                          1.0   
cvmed                                                   0.971558   
cvmode         0    0.647705
Name: trip_duration_seconds, dty...   

column                                  trip_distance_kilometers  
rows                                                        4008  
sum                                                  7081.204667  
mean                                                    1.766768  
median                                                  1.363061  
mode           0    1.355822
Name: trip_distance_kilometers, ...  
max                                                    11.879656  
min                                                     0.100177  
std_dev                                                 1.462954  
variance                                                2.140235  
skewness                                                2.130145  
kurtosis                                                6.883658  
percentile_25                                           0.789487  
percentile_75                                           2.260204  
iqr                                                     1.470717  
range                                                  11.779478  
cv                                                       0.82804  
qd                                                      0.482251  
cs                                                      1.456057  
ck                                                      4.705314  
cvs                                                     1.456057  
cvk                                                     4.705314  
cvcs                                                    1.456057  
cvck                                                    4.705314  
cvcv                                                     0.82804  
cvqd                                                    0.482251  
cvr                                                     6.667248  
cvm                                                          1.0  
cvmed                                                     0.7715  
cvmode         0

In [178]:
# get entries where trips start and end at station
afternoon_delay_next_station_station = afternoon_delay_next[afternoon_delay_next['end_stop_id'].notna() & afternoon_delay_next['start_stop_id'].notna()]
afternoon_delay_next_station_station

nextbike_trips_id nextbike_trips_start_time nextbike_trips_end_time  \
1422827           38000437       2023-07-01 15:01:00     2023-07-01 15:11:00   
1367325           37936293       2023-07-01 15:16:00     2023-07-01 15:41:00   
1473155           37976992       2023-07-01 15:21:00     2023-07-01 15:31:00   
1668986           37800405       2023-07-01 15:21:00     2023-07-01 15:36:00   
1220394           37717933       2023-07-01 15:26:00     2023-07-01 15:41:00   
...                    ...                       ...                     ...   
1259554           37823592       2023-07-31 16:46:00     2023-07-31 16:56:00   
1638348           37769767       2023-07-31 16:51:00     2023-07-31 17:01:00   
1274292           37831022       2023-07-31 16:51:00     2023-07-31 17:11:00   
1332550           37860349       2023-07-31 16:56:00     2023-07-31 17:51:00   
1460547           38027186       2023-07-31 17:01:00     2023-07-31 17:16:00   

         nextbike_trips_start_at_station  nextbike_trips_end_at_station  \
1422827                             True                          False   
1367325                            False                          False   
1473155                            False                          False   
1668986                            False                          False   
1220394                            False                          False   
...                                  ...                            ...   
1259554                            False                          False   
1638348                            False                          False   
1274292                            False                          False   
1332550                            False                          False   
1460547                            False                          False   

        vehicle type   trip_duration  trip_distance_kilometers  \
1422827         bike 0 days 00:10:00                  0.950590   
1367325         bike 0 days 00:25:00                  5.727869   
1473155         bike 0 days 00:10:00                  1.337259   
1668986         bike 0 days 00:15:00                  2.158706   
1220394         bike 0 days 00:15:00                  1.420399   
...              ...             ...                       ...   
1259554         bike 0 days 00:10:00                  2.773151   
1638348         bike 0 days 00:10:00                  0.585929   
1274292         bike 0 days 00:20:00                  1.427347   
1332550         bike 0 days 00:55:00                  0.123326   
1460547         bike 0 days 00:15:00                  1.106455   

         trip_distance_meters  \
1422827            950.590405   
1367325           5727.869332   
1473155           1337.259142   
1668986           2158.705647   
1220394           1420.399488   
...                       ...   
1259554           2773.150597   
1638348            585.928564   
1274292           1427.346859   
1332550            123.325782   
1460547           1106.455028   

                                            start_location  \
1422827  b'\x01\x01\x00\x00\x00\x06.\x8f5#c\x1c@\x9dJ\x...   
1367325  b'\x01\x01\x00\x00\x00\xe7U\x9d\xd5\x02[\x1c@\...   
1473155  b'\x01\x01\x00\x00\x00\t\x8a\x1fc\xeeZ\x1c@\xa...   
1668986  b'\x01\x01\x00\x00\x00\xcc\xd4$xCz\x1c@\xc8\xd...   
1220394  b'\x01\x01\x00\x00\x00\x9f\xe4\x0e\x9b\xc8L\x1...   
...                                                    ...   
1259554  b'\x01\x01\x00\x00\x00\xd3P\xa3\x90df\x1c@\x83...   
1638348  b'\x01\x01\x00\x00\x00\x89%\xe5\xees|\x1c@\x10...   
1274292  b'\x01\x01\x00\x00\x00\xf0\xa5\xf0\xa0\xd9e\x1...   
1332550  b'\x01\x01\x00\x00\x00\xa7\xe8H.\xff1\x1c@*S\x...   
1460547  b'\x01\x01\x00\x00\x00h\xeau\x8b\xc0h\x1c@\xf5...   

                                              end_location  start_stop_id  \
1422827  b'\x01\x01\x00\x00\x00\xf9\xa1\xd2\x88\x99]\x1...         1102.0   
1367325  b'\x01\x01\x00\x00\x00\xb2\x0eGW\xe9\x8e\x1c@\...

In [179]:
afternoon_delay_next_station_station.describe()

nextbike_trips_id      nextbike_trips_start_time  \
count       1.813000e+03                           1813   
mean        3.793642e+07  2023-07-15 19:08:32.564809728   
min         3.771653e+07            2023-07-01 15:01:00   
25%         3.781996e+07            2023-07-08 16:06:00   
50%         3.793756e+07            2023-07-14 15:51:00   
75%         3.804727e+07            2023-07-22 15:11:00   
max         3.817161e+07            2023-07-31 17:01:00   
std         1.286054e+05                            NaN   

             nextbike_trips_end_time              trip_duration  \
count                           1813                       1813   
mean   2023-07-15 19:22:51.858797568  0 days 00:14:19.293987865   
min              2023-07-01 15:11:00            0 days 00:05:00   
25%              2023-07-08 16:21:00            0 days 00:10:00   
50%              2023-07-14 16:01:00            0 days 00:10:00   
75%              2023-07-22 15:26:00            0 days 00:15:00   
max              2023-07-31 17:51:00            0 days 02:00:00   
std                              NaN  0 days 00:09:21.187589048   

       trip_distance_kilometers  trip_distance_meters  start_stop_id  \
count               1813.000000           1813.000000    1813.000000   
mean                   1.466538           1466.538280    1339.548263   
min                    0.100177            100.177408      43.000000   
25%                    0.732464            732.464179    1102.000000   
50%                    1.218382           1218.381963    1140.000000   
75%                    1.927377           1927.376771    1223.000000   
max                    7.425324           7425.324337    9780.000000   
std                    1.089466           1089.466187    1291.296155   

       end_stop_id  trip_duration_seconds  
count  1813.000000            1813.000000  
mean   1367.667402             859.293988  
min      43.000000             300.000000  
25%    1102.000000             600.000000  
50%    1151.000000             600.000000  
75%    1194.000000             900.000000  
max    9703.000000            7200.000000  
std    1419.881810             561.187589

In [180]:
# get statistics for the tier trips that start and end at a station
get_stats(afternoon_delay_next_station_station, ['trip_duration_seconds', 'trip_distance_kilometers'])

column                                     trip_duration_seconds  \
rows                                                        1813   
sum                                                    1557900.0   
mean                                                  859.293988   
median                                                     600.0   
mode           0    600.0
Name: trip_duration_seconds, dtype:...   
max                                                       7200.0   
min                                                        300.0   
std_dev                                               561.187589   
variance                                           314931.510102   
skewness                                                3.889277   
kurtosis                                               25.174933   
percentile_25                                              600.0   
percentile_75                                              900.0   
iqr                                                        300.0   
range                                                     6900.0   
cv                                                       0.65308   
qd                                                           0.2   
cs                                                       0.00693   
ck                                                       0.04486   
cvs                                                      0.00693   
cvk                                                      0.04486   
cvcs                                                     0.00693   
cvck                                                     0.04486   
cvcv                                                     0.65308   
cvqd                                                         0.2   
cvr                                                     8.029848   
cvm                                                          1.0   
cvmed                                                   0.698248   
cvmode         0    0.698248
Name: trip_duration_seconds, dty...   

column                                  trip_distance_kilometers  
rows                                                        1813  
sum                                                  2658.833902  
mean                                                    1.466538  
median                                                  1.218382  
mode           0    1.355822
Name: trip_distance_kilometers, ...  
max                                                     7.425324  
min                                                     0.100177  
std_dev                                                 1.089466  
variance                                                1.186937  
skewness                                                1.763524  
kurtosis                                                4.321794  
percentile_25                                           0.732464  
percentile_75                                           1.927377  
iqr                                                     1.194913  
range                                                   7.325147  
cv                                                      0.742883  
qd                                                      0.449242  
cs                                                      1.618704  
ck                                                      3.966892  
cvs                                                     1.618704  
cvk                                                     3.966892  
cvcs                                                    1.618704  
cvck                                                    3.966892  
cvcv                                                    0.742883  
cvqd                                                    0.449242  
cvr                                                     4.994856  
cvm                                                          1.0  
cvmed                                                   0.830788  
cvmode         0

In [181]:
afternoon_no_delay = no_delay[(no_delay['scheduled_arrival_time'].dt.hour > 14) & (no_delay['scheduled_arrival_time'].dt.hour < 17)]
afternoon_no_delay

route_id  agency_id route_short_name  route_type route_type_name  \
43972          65          6               65           0            Tram   
43976         613          6              613           3             Bus   
43982         609          6              609           3             Bus   
43984         845         12              845           3             Bus   
43991          63          6               63           0            Tram   
...           ...        ...              ...         ...             ...   
2533581       537          8              537           3             Bus   
2533584       537          8              537           3             Bus   
2533601       610          6              610           3             Bus   
2533607       606          6              606           3             Bus   
2533619       843         12              843           3             Bus   

                                         agency_name  service_id  \
43972              SWB Stadtwerke Bonn Verkehrs GmbH       26814   
43976              SWB Stadtwerke Bonn Verkehrs GmbH         130   
43982              SWB Stadtwerke Bonn Verkehrs GmbH         130   
43984    RVK Regionalverkehr Köln GmbH NL Meckenheim         130   
43991              SWB Stadtwerke Bonn Verkehrs GmbH          43   
...                                              ...         ...   
2533581     RSVG Rhein-Sieg-Verkehrsgesellschaft mbH          64   
2533584     RSVG Rhein-Sieg-Verkehrsgesellschaft mbH          64   
2533601            SWB Stadtwerke Bonn Verkehrs GmbH          64   
2533607            SWB Stadtwerke Bonn Verkehrs GmbH          64   
2533619  RVK Regionalverkehr Köln GmbH NL Meckenheim       27690   

                                                   trip_id  \
43972    650718-65-006-1406.1.12:143400-24-178_32CE736F...   
43976    6130311-613-006-1756.2.21:142900-27-1_D3734311...   
43982    6090184-609-006-1574.2.24:150000-45-1_8F749382...   
43984    1027-845-012-687.2.28:144800-29-1_6224B816-48F...   
43991    630048-63-006-694.1.12:150000-18-1_78DD6CEA-C4...   
...                                                    ...   
2533581  25-537-008-2140.2.21:163200-36-1_615482EB-2673...   
2533584  111-537-008-687.2.36:163600-37-1_E04DACAC-6FDA...   
2533601  6100099-610-006-1756.2.21:162600-54-1_2105D5E3...   
2533607  6060112-606-006-1584.2.22:161200-44-1_B8E2590C...   
2533619  52-843-012-8845.2.24:163500-38-1_8542C353-A41F...   

                       trip_headsign  direction_id  ...  delay_span  \
43972    Oberkassel Süd/Römlinghoven             1  ...         0-5   
43976                      Pappelweg             0  ...           0   
43982             Hardthöhe/Südwache             1  ...           0   
43984                        Fronhof             0  ...           0   
43991       Bad Godesberg Stadthalle             1  ...           0   
...                              ...           ...  ...         ...   
2533581                     Bonn Hbf             0  ...           0   
2533584              Oberpleis Busbf             1  ...           0   
2533601                  Duisdorf Bf             0  ...         0-5   
2533607           Hardtberg Klinikum             1  ...           0   
2533619                 Hertersplatz             1  ...           0   

         arrival_delay_span weather_int time_span_arrival  \
43972                     0           0                 0   
43976                     0           0             lunch   
43982                     0           0                 0   
43984                     0           0                 0   
43991                     0           0                 0   
...                     ...         ...               ...   
2533581                   0           1         afternoon   
2533584                   0           1         afternoon   
2533601                   0           1                 0   
2533607                   0           1         afternoon  

In [182]:
get_stats(afternoon_no_delay, ['tier_trips_count', 'tier_trips_end_at_station_count', 'nextbike_trips_count', 'nextbike_trips_end_at_station_count', 'current_temp', 'current_precipitation_volume'])

/tmp/ipykernel_2575952/41814695.py:51: RuntimeWarning: invalid value encountered in scalar divide
  qd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:55: RuntimeWarning: invalid value encountered in scalar divide
  cvqd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:51: RuntimeWarning: invalid value encountered in scalar divide
  qd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:55: RuntimeWarning: invalid value encountered in scalar divide
  cvqd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:51: RuntimeWarning: invalid value encountered in scalar divide
  qd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:55: RuntimeWarning: invalid value encountered in scalar divide
  cvqd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:51: RuntimeWarning: invalid value encountered in scalar divide
  qd = iqr / (percentile_75 + percenti

column                                        tier_trips_count  \
rows                                                     67154   
sum                                                       3005   
mean                                                  0.044748   
median                                                     0.0   
mode               0    0
Name: tier_trips_count, dtype: int64   
max                                                          4   
min                                                          0   
std_dev                                               0.248311   
variance                                              0.061658   
skewness                                              7.220198   
kurtosis                                             68.986192   
percentile_25                                              0.0   
percentile_75                                              0.0   
iqr                                                        0.0   
range                                                        4   
cv                                                    5.549103   
qd                                                         NaN   
cs                                                   29.077277   
ck                                                  277.822094   
cvs                                                  29.077277   
cvk                                                 277.822094   
cvcs                                                 29.077277   
cvck                                                277.822094   
cvcv                                                  5.549103   
cvqd                                                       NaN   
cvr                                                  89.389684   
cvm                                                        1.0   
cvmed                                                      0.0   
cvmode         0    0.0
Name: tier_trips_count, dtype: float64   

column                           tier_trips_end_at_station_count  \
rows                                                       67154   
sum                                                         2467   
mean                                                    0.036736   
median                                                       0.0   
mode           0    0
Name: tier_trips_end_at_station_count, ...   
max                                                            4   
min                                                            0   
std_dev                                                 0.224163   
variance                                                0.050249   
skewness                                                7.985052   
kurtosis                                               85.366695   
percentile_25                                                0.0   
percentile_75                                                0.0   
iqr                                                          0.0   
range                                                          4   
cv                                                      6.101919   
qd                                                           NaN   
cs                                                     35.621648   
ck                                                    380.824389   
cvs                                                    35.621648   
cvk                                                   380.824389   
cvcs                                                   35.621648   
cvck                                                  380.824389   
cvcv                                                    6.101919   
cvqd                                                         NaN   
cvr                                                   108.883664   
cvm                                                          1.0   
cvmed                                                        0.0   
cvmode         0    0.0
Name: tier_trips_end_at

In [183]:
afternoon_no_delay_tier = check_micromobility_datasets('tier', afternoon_no_delay)

In [184]:
afternoon_no_delay_tier.describe()

tier_trips_id          tier_trips_start_time  \
count   1.175000e+03                           1175   
mean    7.990314e+08  2023-07-15 14:18:20.936170240   
min     7.822646e+08            2023-07-01 15:05:00   
25%     7.823709e+08            2023-07-07 16:35:00   
50%     8.086378e+08            2023-07-14 15:20:00   
75%     8.087496e+08            2023-07-22 15:50:00   
max     8.323114e+08            2023-07-31 17:00:00   
std     1.641262e+07                            NaN   

                 tier_trips_end_time              trip_duration  \
count                           1175                       1175   
mean   2023-07-15 14:32:42.127659520  0 days 00:14:21.191489361   
min              2023-07-01 15:15:00            0 days 00:05:00   
25%              2023-07-07 16:52:30            0 days 00:10:00   
50%              2023-07-14 15:30:00            0 days 00:10:00   
75%              2023-07-22 16:05:00            0 days 00:15:00   
max              2023-07-31 18:20:00            0 days 01:55:00   
std                              NaN  0 days 00:10:24.070233070   

       trip_distance_kilometers  trip_distance_meters  start_stop_id  \
count               1175.000000           1175.000000     909.000000   
mean                   1.758156           1758.155760    1184.334433   
min                    0.100067            100.066815      43.000000   
25%                    0.727732            727.731639     687.000000   
50%                    1.330009           1330.008998    1110.000000   
75%                    2.216827           2216.826957    1382.000000   
max                   12.402037          12402.036677    9702.000000   
std                    1.546782           1546.781598    1061.381276   

       end_stop_id  trip_duration_seconds  
count   550.000000            1175.000000  
mean   1308.867273             861.191489  
min      43.000000             300.000000  
25%    1102.000000             600.000000  
50%    1144.000000             600.000000  
75%    1224.000000             900.000000  
max    9703.000000            6900.000000  
std    1181.993640             624.070233

In [185]:
get_stats(afternoon_no_delay_tier, ['trip_duration_seconds', 'trip_distance_kilometers'])

column                                     trip_duration_seconds  \
rows                                                        1175   
sum                                                    1011900.0   
mean                                                  861.191489   
median                                                     600.0   
mode           0    600.0
Name: trip_duration_seconds, dtype:...   
max                                                       6900.0   
min                                                        300.0   
std_dev                                               624.070233   
variance                                           389463.655805   
skewness                                                4.067765   
kurtosis                                               25.719986   
percentile_25                                              600.0   
percentile_75                                              900.0   
iqr                                                        300.0   
range                                                     6600.0   
cv                                                      0.724659   
qd                                                           0.2   
cs                                                      0.006518   
ck                                                      0.041213   
cvs                                                     0.006518   
cvk                                                     0.041213   
cvcs                                                    0.006518   
cvck                                                    0.041213   
cvcv                                                    0.724659   
cvqd                                                         0.2   
cvr                                                     7.663801   
cvm                                                          1.0   
cvmed                                                   0.696709   
cvmode         0    0.696709
Name: trip_duration_seconds, dty...   

column                                  trip_distance_kilometers  
rows                                                        1175  
sum                                                  2065.833018  
mean                                                    1.758156  
median                                                  1.330009  
mode           0        0.100067
1        0.100253
2        0...  
max                                                    12.402037  
min                                                     0.100067  
std_dev                                                 1.546782  
variance                                                2.392533  
skewness                                                2.056454  
kurtosis                                                5.743364  
percentile_25                                           0.727732  
percentile_75                                           2.216827  
iqr                                                     1.489095  
range                                                   12.30197  
cv                                                      0.879775  
qd                                                      0.505711  
cs                                                      1.329505  
ck                                                      3.713106  
cvs                                                     1.329505  
cvk                                                     3.713106  
cvcs                                                    1.329505  
cvck                                                    3.713106  
cvcv                                                    0.879775  
cvqd                                                    0.505711  
cvr                                                     6.997088  
cvm                                                          1.0  
cvmed                                                    0.75648  
cvmode         0

In [186]:
# get entries where trips start and end at station
afternoon_no_delay_tier_station_station = afternoon_no_delay_tier[afternoon_no_delay_tier['end_stop_id'].notna() & afternoon_no_delay_tier['start_stop_id'].notna()]
afternoon_no_delay_tier_station_station

tier_trips_id tier_trips_start_time tier_trips_end_time vehicle type  \
3164081      782350087   2023-07-01 15:05:00 2023-07-01 15:15:00    e-scooter   
3251887      782429950   2023-07-01 15:25:00 2023-07-01 15:35:00    e-scooter   
3261302      782438438   2023-07-01 15:25:00 2023-07-01 15:35:00    e-scooter   
3165478      782351003   2023-07-01 15:35:00 2023-07-01 15:45:00    e-scooter   
3251889      782429952   2023-07-01 15:55:00 2023-07-01 16:00:00    e-scooter   
...                ...                   ...                 ...          ...   
3514366      832293399   2023-07-31 15:55:00 2023-07-31 16:05:00    e-scooter   
3518638      832297518   2023-07-31 15:55:00 2023-07-31 16:15:00    e-scooter   
3437216      832219346   2023-07-31 16:35:00 2023-07-31 16:40:00    e-scooter   
3338340      832133612   2023-07-31 16:50:00 2023-07-31 17:00:00    e-scooter   
3305017      832110902   2023-07-31 17:00:00 2023-07-31 18:20:00    e-scooter   

          trip_duration  trip_distance_kilometers  trip_distance_meters  \
3164081 0 days 00:10:00                  1.020358           1020.357721   
3251887 0 days 00:10:00                  1.023885           1023.884767   
3261302 0 days 00:10:00                  0.286699            286.699142   
3165478 0 days 00:10:00                  0.848609            848.608825   
3251889 0 days 00:05:00                  0.169607            169.606983   
...                 ...                       ...                   ...   
3514366 0 days 00:10:00                  0.875062            875.062283   
3518638 0 days 00:20:00                  1.765479           1765.479372   
3437216 0 days 00:05:00                  0.260465            260.465466   
3338340 0 days 00:10:00                  0.266824            266.823960   
3305017 0 days 01:20:00                  0.257841            257.841257   

         start_stop_id                            start_stop_name  \
3164081         1162.0                              Bonn Rosental   
3251887          687.0                                   Bonn Hbf   
3261302         1144.0                         Bonn Beethovenstr.   
3165478         1153.0                              Bonn Heerstr.   
3251889          686.0                     Bonn Universität/Markt   
...                ...                                        ...   
3514366         1104.0                             Bonn Stadthaus   
3518638         1500.0                 Bonn Konrad-Adenauer-Platz   
3437216          687.0                                   Bonn Hbf   
3338340         1115.0  Bonn Bertha-Von-Suttner-Pl./Beethovenhaus   
3305017          687.0                                   Bonn Hbf   

                                         start_buffer_zone  end_stop_id  \
3164081  801621     POLYGON ((7.157885983913106 50.7227...       1181.0   
3251887  801621     POLYGON ((7.157885983913106 50.7227...       1224.0   
3261302  801621     POLYGON ((7.157885983913106 50.7227...        687.0   
3165478  801621     POLYGON ((7.157885983913106 50.7227...       1106.0   
3251889  801621     POLYGON ((7.157885983913106 50.7227...        686.0   
...                                                    ...          ...   
3514366  801621     POLYGON ((7.157885983913106 50.7227...       1144.0   
3518638  801621     POLYGON ((7.157885983913106 50.7227...       1115.0   
3437216  801621     POLYGON ((7.157885983913106 50.7227...        686.0   
3338340  801621     POLYGON ((7.157885983913106 50.7227...       2667.0   
3305017  801621     POLYGON ((7.157885983913106 50.7227...       1106.0   

                                     end_stop_name  \
3164081                           Bonn Am Nordpark   
3251887                 Bonn Am Botanischen Garten   
3261302                                   Bonn Hbf   
3165478                      Bonn Thomas-Mann-Str.   
3251889                     Bonn Universität/Markt   
...                                            ...   
3514366                    

In [187]:
afternoon_no_delay_tier_station_station.describe()

tier_trips_id          tier_trips_start_time  \
count   4.930000e+02                            493   
mean    7.981524e+08  2023-07-15 03:10:02.434077184   
min     7.822652e+08            2023-07-01 15:05:00   
25%     7.823561e+08            2023-07-07 16:45:00   
50%     8.086284e+08            2023-07-13 15:50:00   
75%     8.087325e+08            2023-07-22 15:05:00   
max     8.323095e+08            2023-07-31 17:00:00   
std     1.634487e+07                            NaN   

                 tier_trips_end_time              trip_duration  \
count                            493                        493   
mean   2023-07-15 03:23:34.198782720  0 days 00:13:31.764705882   
min              2023-07-01 15:15:00            0 days 00:05:00   
25%              2023-07-07 16:55:00            0 days 00:10:00   
50%              2023-07-13 16:00:00            0 days 00:10:00   
75%              2023-07-22 15:15:00            0 days 00:15:00   
max              2023-07-31 18:20:00            0 days 01:55:00   
std                              NaN  0 days 00:10:57.928142321   

       trip_distance_kilometers  trip_distance_meters  start_stop_id  \
count                493.000000            493.000000     493.000000   
mean                   1.475512           1475.511702    1230.498986   
min                    0.100067            100.066815      43.000000   
25%                    0.621032            621.032033     687.000000   
50%                    1.089977           1089.976635    1115.000000   
75%                    1.937608           1937.607922    1292.000000   
max                    8.717363           8717.363368    9702.000000   
std                    1.337842           1337.841812    1020.762824   

       end_stop_id  trip_duration_seconds  
count   493.000000             493.000000  
mean   1330.006085             811.764706  
min      43.000000             300.000000  
25%    1102.000000             600.000000  
50%    1144.000000             600.000000  
75%    1224.000000             900.000000  
max    9703.000000            6900.000000  
std    1229.968209             657.928142

In [188]:
# get statistics for the tier trips that start and end at a station
get_stats(afternoon_no_delay_tier_station_station, ['trip_duration_seconds', 'trip_distance_kilometers'])

column                                     trip_duration_seconds  \
rows                                                         493   
sum                                                     400200.0   
mean                                                  811.764706   
median                                                     600.0   
mode           0    600.0
Name: trip_duration_seconds, dtype:...   
max                                                       6900.0   
min                                                        300.0   
std_dev                                               657.928142   
variance                                           432869.440459   
skewness                                                5.027589   
kurtosis                                               35.635435   
percentile_25                                              600.0   
percentile_75                                              900.0   
iqr                                                        300.0   
range                                                     6600.0   
cv                                                      0.810491   
qd                                                           0.2   
cs                                                      0.007642   
ck                                                      0.054163   
cvs                                                     0.007642   
cvk                                                     0.054163   
cvcs                                                    0.007642   
cvck                                                    0.054163   
cvcv                                                    0.810491   
cvqd                                                         0.2   
cvr                                                     8.130435   
cvm                                                          1.0   
cvmed                                                    0.73913   
cvmode         0    0.73913
Name: trip_duration_seconds, dtyp...   

column                                  trip_distance_kilometers  
rows                                                         493  
sum                                                   727.427269  
mean                                                    1.475512  
median                                                  1.089977  
mode           0      0.100067
1      0.100253
2      0.10486...  
max                                                     8.717363  
min                                                     0.100067  
std_dev                                                 1.337842  
variance                                                1.789821  
skewness                                                2.372298  
kurtosis                                                7.794712  
percentile_25                                           0.621032  
percentile_75                                           1.937608  
iqr                                                     1.316576  
range                                                   8.617297  
cv                                                      0.906697  
qd                                                      0.514561  
cs                                                      1.773228  
ck                                                      5.826333  
cvs                                                     1.773228  
cvk                                                     5.826333  
cvcs                                                    1.773228  
cvck                                                    5.826333  
cvcv                                                    0.906697  
cvqd                                                    0.514561  
cvr                                                     5.840209  
cvm                                                          1.0  
cvmed                                                   0.738711  
cvmode         0

In [189]:
afternoon_no_delay_next = check_micromobility_datasets('next', afternoon_no_delay)

In [190]:
afternoon_no_delay_next.describe()

nextbike_trips_id      nextbike_trips_start_time  \
count       3.008000e+03                           3008   
mean        3.793910e+07  2023-07-16 04:29:42.706116864   
min         3.771654e+07            2023-07-01 15:01:00   
25%         3.782660e+07            2023-07-08 16:16:00   
50%         3.794252e+07            2023-07-15 16:48:30   
75%         3.804853e+07            2023-07-22 16:41:00   
max         3.817162e+07            2023-07-31 17:01:00   
std         1.282169e+05                            NaN   

             nextbike_trips_end_time              trip_duration  \
count                           3008                       3008   
mean   2023-07-16 04:44:58.663564032  0 days 00:15:15.957446808   
min              2023-07-01 15:11:00            0 days 00:05:00   
25%              2023-07-08 16:36:00            0 days 00:10:00   
50%              2023-07-15 17:06:00            0 days 00:15:00   
75%              2023-07-22 17:01:00            0 days 00:15:00   
max              2023-07-31 17:11:00            0 days 02:00:00   
std                              NaN  0 days 00:10:40.894900027   

       trip_distance_kilometers  trip_distance_meters  start_stop_id  \
count               3008.000000           3008.000000    2500.000000   
mean                   1.727999           1727.998970    1131.724000   
min                    0.100458            100.458077      43.000000   
25%                    0.788296            788.295717     687.000000   
50%                    1.307553           1307.553140    1102.000000   
75%                    2.184073           2184.072675    1175.000000   
max                   11.879656          11879.655514    9780.000000   
std                    1.475813           1475.812652    1120.515913   

       end_stop_id  trip_duration_seconds  
count  1651.000000            3008.000000  
mean   1267.310721             915.957447  
min      43.000000             300.000000  
25%    1103.000000             600.000000  
50%    1151.000000             900.000000  
75%    1221.000000             900.000000  
max    9702.000000            7200.000000  
std    1104.692654             640.894900

In [191]:
get_stats(afternoon_no_delay_next, ['trip_duration_seconds', 'trip_distance_kilometers'])

column                                     trip_duration_seconds  \
rows                                                        3008   
sum                                                    2755200.0   
mean                                                  915.957447   
median                                                     900.0   
mode           0    600.0
Name: trip_duration_seconds, dtype:...   
max                                                       7200.0   
min                                                        300.0   
std_dev                                                 640.8949   
variance                                           410746.272881   
skewness                                                4.056411   
kurtosis                                               26.762419   
percentile_25                                              600.0   
percentile_75                                              900.0   
iqr                                                        300.0   
range                                                     6900.0   
cv                                                      0.699699   
qd                                                           0.2   
cs                                                      0.006329   
ck                                                      0.041758   
cvs                                                     0.006329   
cvk                                                     0.041758   
cvcs                                                    0.006329   
cvck                                                    0.041758   
cvcv                                                    0.699699   
cvqd                                                         0.2   
cvr                                                     7.533101   
cvm                                                          1.0   
cvmed                                                   0.982578   
cvmode         0    0.655052
Name: trip_duration_seconds, dty...   

column                                  trip_distance_kilometers  
rows                                                        3008  
sum                                                  5197.820902  
mean                                                    1.727999  
median                                                  1.307553  
mode           0    0.17361
Name: trip_distance_kilometers, d...  
max                                                    11.879656  
min                                                     0.100458  
std_dev                                                 1.475813  
variance                                                2.178023  
skewness                                                2.181701  
kurtosis                                                6.594423  
percentile_25                                           0.788296  
percentile_75                                           2.184073  
iqr                                                     1.395777  
range                                                  11.779197  
cv                                                      0.854059  
qd                                                      0.469584  
cs                                                      1.478305  
ck                                                      4.468333  
cvs                                                     1.478305  
cvk                                                     4.468333  
cvcs                                                    1.478305  
cvck                                                    4.468333  
cvcv                                                    0.854059  
cvqd                                                    0.469584  
cvr                                                     6.816669  
cvm                                                          1.0  
cvmed                                                   0.756686  
cvmode         0

In [192]:
# get entries where trips start and end at station
afternoon_no_delay_next_station_station = afternoon_no_delay_next[afternoon_no_delay_next['end_stop_id'].notna() & afternoon_no_delay_next['start_stop_id'].notna()]
afternoon_no_delay_next_station_station

nextbike_trips_id nextbike_trips_start_time nextbike_trips_end_time  \
1385918           37921942       2023-07-01 15:01:00     2023-07-01 15:26:00   
1269798           37830066       2023-07-01 15:01:00     2023-07-01 15:16:00   
1631336           37762755       2023-07-01 15:01:00     2023-07-01 15:11:00   
1565270           38115852       2023-07-01 15:06:00     2023-07-01 15:16:00   
1377784           37917346       2023-07-01 15:06:00     2023-07-01 15:36:00   
...                    ...                       ...                     ...   
1246870           37818216       2023-07-31 16:16:00     2023-07-31 16:26:00   
1562831           38166959       2023-07-31 16:21:00     2023-07-31 16:26:00   
1531046           38082061       2023-07-31 16:31:00     2023-07-31 16:41:00   
1391497           37923983       2023-07-31 16:56:00     2023-07-31 17:06:00   
1531048           38082063       2023-07-31 16:56:00     2023-07-31 17:06:00   

         nextbike_trips_start_at_station  nextbike_trips_end_at_station  \
1385918                            False                          False   
1269798                             True                          False   
1631336                             True                           True   
1565270                            False                          False   
1377784                            False                          False   
...                                  ...                            ...   
1246870                            False                          False   
1562831                            False                          False   
1531046                            False                           True   
1391497                            False                          False   
1531048                            False                          False   

        vehicle type   trip_duration  trip_distance_kilometers  \
1385918         bike 0 days 00:25:00                  4.469206   
1269798         bike 0 days 00:15:00                  1.041941   
1631336         bike 0 days 00:10:00                  1.415742   
1565270         bike 0 days 00:10:00                  0.800215   
1377784         bike 0 days 00:30:00                  1.774788   
...              ...             ...                       ...   
1246870         bike 0 days 00:10:00                  1.022421   
1562831         bike 0 days 00:05:00                  0.824348   
1531046         bike 0 days 00:10:00                  0.413295   
1391497         bike 0 days 00:10:00                  1.469302   
1531048         bike 0 days 00:10:00                  0.473075   

         trip_distance_meters  \
1385918           4469.205983   
1269798           1041.941303   
1631336           1415.741816   
1565270            800.214913   
1377784           1774.787687   
...                       ...   
1246870           1022.420851   
1562831            824.347539   
1531046            413.294604   
1391497           1469.302141   
1531048            473.075103   

                                            start_location  \
1385918  b'\x01\x01\x00\x00\x00\x1dut\\\x8dl\x1c@u<f\xa...   
1269798  b'\x01\x01\x00\x00\x00R\x81\x93m\xe0n\x1c@}\x9...   
1631336  b'\x01\x01\x00\x00\x00R\x81\x93m\xe0n\x1c@}\x9...   
1565270   b'\x01\x01\x00\x00\x00uYLl>.\x1c@U\xde\x8epZ`I@'   
1377784  b'\x01\x01\x00\x00\x00\xc8\xd2\x87.\xa8_\x1c@L...   
...                                                    ...   
1246870  b'\x01\x01\x00\x00\x00\xacX\xfc\xa6\xb0b\x1c@\...   
1562831  b'\x01\x01\x00\x00\x00\xd3\xbdN\xea\xcbb\x1c@\...   
1531046  b'\x01\x01\x00\x00\x00u\xccy\xc6\xbed\x1c@wN\x...   
1391497  b'\x01\x01\x00\x00\x00\x9b\xaf\x92\x8f\xddU\x1...   
1531048  b'\x01\x01\x00\x00\x00e\xe2VA\x0cd\x1c@\x96\xc...   

                                              end_location  start_stop_id  \
1385918  b'\x01\x01\x00\x00\x00M\xdc*\x88\x81\x8e\x1c@\...         2667.0   
1269798  b'\x01\x01\x00\x00\x006\xca\xfa\xcd\xc4t\x1c@\...

In [193]:
afternoon_no_delay_next_station_station.describe()

nextbike_trips_id      nextbike_trips_start_time  \
count       1.473000e+03                           1473   
mean        3.793883e+07  2023-07-16 01:51:22.199592448   
min         3.771658e+07            2023-07-01 15:01:00   
25%         3.782719e+07            2023-07-08 15:41:00   
50%         3.793951e+07            2023-07-14 17:01:00   
75%         3.804854e+07            2023-07-22 16:51:00   
max         3.817158e+07            2023-07-31 16:56:00   
std         1.280032e+05                            NaN   

             nextbike_trips_end_time              trip_duration  \
count                           1473                       1473   
mean   2023-07-16 02:05:24.562118144  0 days 00:14:02.362525458   
min              2023-07-01 15:11:00            0 days 00:05:00   
25%              2023-07-08 15:56:00            0 days 00:10:00   
50%              2023-07-14 19:01:00            0 days 00:10:00   
75%              2023-07-22 17:06:00            0 days 00:15:00   
max              2023-07-31 17:06:00            0 days 02:00:00   
std                              NaN  0 days 00:09:26.055537207   

       trip_distance_kilometers  trip_distance_meters  start_stop_id  \
count               1473.000000           1473.000000    1473.000000   
mean                   1.402652           1402.652329    1194.581806   
min                    0.100458            100.458077      43.000000   
25%                    0.712656            712.656030     687.000000   
50%                    1.109645           1109.645257    1103.000000   
75%                    1.716556           1716.555597    1174.000000   
max                    8.255968           8255.968494    9780.000000   
std                    1.094506           1094.505842    1259.058850   

       end_stop_id  trip_duration_seconds  
count  1473.000000            1473.000000  
mean   1292.558045             842.362525  
min      43.000000             300.000000  
25%    1106.000000             600.000000  
50%    1151.000000             600.000000  
75%    1221.000000             900.000000  
max    9702.000000            7200.000000  
std    1125.914133             566.055537

In [194]:
# get statistics for the tier trips that start and end at a station
get_stats(afternoon_no_delay_next_station_station, ['trip_duration_seconds', 'trip_distance_kilometers'])

column                                     trip_duration_seconds  \
rows                                                        1473   
sum                                                    1240800.0   
mean                                                  842.362525   
median                                                     600.0   
mode           0    600.0
Name: trip_duration_seconds, dtype:...   
max                                                       7200.0   
min                                                        300.0   
std_dev                                               566.055537   
variance                                           320418.871203   
skewness                                                4.253225   
kurtosis                                               30.205727   
percentile_25                                              600.0   
percentile_75                                              900.0   
iqr                                                        300.0   
range                                                     6900.0   
cv                                                      0.671986   
qd                                                           0.2   
cs                                                      0.007514   
ck                                                      0.053362   
cvs                                                     0.007514   
cvk                                                     0.053362   
cvcs                                                    0.007514   
cvck                                                    0.053362   
cvcv                                                    0.671986   
cvqd                                                         0.2   
cvr                                                     8.191248   
cvm                                                          1.0   
cvmed                                                   0.712282   
cvmode         0    0.712282
Name: trip_duration_seconds, dty...   

column                                  trip_distance_kilometers  
rows                                                        1473  
sum                                                  2066.106881  
mean                                                    1.402652  
median                                                  1.109645  
mode           0    2.896818
Name: trip_distance_kilometers, ...  
max                                                     8.255968  
min                                                     0.100458  
std_dev                                                 1.094506  
variance                                                1.197943  
skewness                                                2.100329  
kurtosis                                                 6.02669  
percentile_25                                           0.712656  
percentile_75                                           1.716556  
iqr                                                       1.0039  
range                                                    8.15551  
cv                                                      0.780312  
qd                                                      0.413261  
cs                                                      1.918975  
ck                                                      5.506311  
cvs                                                     1.918975  
cvk                                                     5.506311  
cvcs                                                    1.918975  
cvck                                                    5.506311  
cvcv                                                    0.780312  
cvqd                                                    0.413261  
cvr                                                     5.814349  
cvm                                                          1.0  
cvmed                                                   0.791105  
cvmode         0

In [195]:
afternoon_nan_delay = nan_delay[(nan_delay['scheduled_arrival_time'].dt.hour > 14) & (nan_delay['scheduled_arrival_time'].dt.hour < 17)]
afternoon_nan_delay

route_id  agency_id route_short_name  route_type route_type_name  \
43973         607          6              607           3             Bus   
43974         605          6              605           3             Bus   
43975         605          6              605           3             Bus   
43977         602          6              602           3             Bus   
43979         605          6              605           3             Bus   
...           ...        ...              ...         ...             ...   
2533609       640          6              640           3             Bus   
2533612       600          6              600           3             Bus   
2533613       605          6              605           3             Bus   
2533615       640          6              640           3             Bus   
2533617        65          6               65           0            Tram   

                               agency_name  service_id  \
43973    SWB Stadtwerke Bonn Verkehrs GmbH         130   
43974    SWB Stadtwerke Bonn Verkehrs GmbH         130   
43975    SWB Stadtwerke Bonn Verkehrs GmbH         130   
43977    SWB Stadtwerke Bonn Verkehrs GmbH         130   
43979    SWB Stadtwerke Bonn Verkehrs GmbH         130   
...                                    ...         ...   
2533609  SWB Stadtwerke Bonn Verkehrs GmbH          64   
2533612  SWB Stadtwerke Bonn Verkehrs GmbH          64   
2533613  SWB Stadtwerke Bonn Verkehrs GmbH          64   
2533615  SWB Stadtwerke Bonn Verkehrs GmbH          64   
2533617  SWB Stadtwerke Bonn Verkehrs GmbH       26825   

                                                   trip_id  \
43973    6070171-607-006-1357.2.21:141100-45-1_1A455642...   
43974    6050167-605-006-1341.2.24:142700-40-1_5CD2567B...   
43975    6050169-605-006-1341.2.24:144700-40-1_36D956C8...   
43977    6020186-602-006-9478.2.22:145800-39-1_F2B4047E...   
43979    6050165-605-006-1341.2.24:140700-40-1_DA81D598...   
...                                                    ...   
2533609  6400072-640-006-1811.2.25:163300-33-1_3ECDA9F3...   
2533612  6000066-600-006-8813.2.22:161800-32-1_80FAED6B...   
2533613  6050101-605-006-1341.2.24:160600-40-1_5D0B5E7C...   
2533615  6400070-640-006-1811.2.25:161300-33-1_F3EB3D51...   
2533617  651091-65-006-1593.1.12:163400-24-179_3CA7FF4E...   

               trip_headsign  direction_id  ...  delay_span  \
43973             Ramersdorf             0  ...           0   
43974        Mondorfer Fähre             0  ...           0   
43975        Mondorfer Fähre             0  ...           0   
43977                 Waldau             1  ...           0   
43979        Mondorfer Fähre             0  ...           0   
...                      ...           ...  ...         ...   
2533609             Bonn Hbf             1  ...           0   
2533612  Ippendorf Altenheim             1  ...           0   
2533613      Mondorfer Fähre             0  ...           0   
2533615             Bonn Hbf             1  ...           0   
2533617    Kopenhagener Str.             0  ...           0   

         arrival_delay_span weather_int time_span_arrival  \
43973                     0           0                 0   
43974                     0           0                 0   
43975                     0           0                 0   
43977                     0           0                 0   
43979                     0           0                 0   
...                     ...         ...               ...   
2533609                   0           1                 0   
2533612                   0           1                 0   
2533613                   0           1                 0   
2533615                   0           1                 0   
2533617                   0           1                 0   

         time_span_int_arrival  weekend time_span time_span_int  \
43973                        0        2         0             0   
43974             

In [196]:
get_stats(afternoon_nan_delay, ['tier_trips_count', 'tier_trips_end_at_station_count', 'nextbike_trips_count', 'nextbike_trips_end_at_station_count', 'current_temp', 'current_precipitation_volume'])

/tmp/ipykernel_2575952/41814695.py:51: RuntimeWarning: invalid value encountered in scalar divide
  qd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:55: RuntimeWarning: invalid value encountered in scalar divide
  cvqd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:51: RuntimeWarning: invalid value encountered in scalar divide
  qd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:55: RuntimeWarning: invalid value encountered in scalar divide
  cvqd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:51: RuntimeWarning: invalid value encountered in scalar divide
  qd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:55: RuntimeWarning: invalid value encountered in scalar divide
  cvqd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:51: RuntimeWarning: invalid value encountered in scalar divide
  qd = iqr / (percentile_75 + percenti

column                                        tier_trips_count  \
rows                                                    127187   
sum                                                       3440   
mean                                                  0.027047   
median                                                     0.0   
mode               0    0
Name: tier_trips_count, dtype: int64   
max                                                          4   
min                                                          0   
std_dev                                               0.180439   
variance                                              0.032558   
skewness                                              7.884966   
kurtosis                                             78.995815   
percentile_25                                              0.0   
percentile_75                                              0.0   
iqr                                                        0.0   
range                                                        4   
cv                                                    6.671371   
qd                                                         NaN   
cs                                                    43.69875   
ck                                                  437.797496   
cvs                                                   43.69875   
cvk                                                 437.797496   
cvcs                                                  43.69875   
cvck                                                437.797496   
cvcv                                                  6.671371   
cvqd                                                       NaN   
cvr                                                  147.89186   
cvm                                                        1.0   
cvmed                                                      0.0   
cvmode         0    0.0
Name: tier_trips_count, dtype: float64   

column                           tier_trips_end_at_station_count  \
rows                                                      127187   
sum                                                         2771   
mean                                                    0.021787   
median                                                       0.0   
mode           0    0
Name: tier_trips_end_at_station_count, ...   
max                                                            4   
min                                                            0   
std_dev                                                  0.16163   
variance                                                0.026124   
skewness                                                8.864573   
kurtosis                                              102.149428   
percentile_25                                                0.0   
percentile_75                                                0.0   
iqr                                                          0.0   
range                                                          4   
cv                                                      7.418694   
qd                                                           NaN   
cs                                                     54.844938   
ck                                                    631.996517   
cvs                                                    54.844938   
cvk                                                   631.996517   
cvcs                                                   54.844938   
cvck                                                  631.996517   
cvcv                                                    7.418694   
cvqd                                                         NaN   
cvr                                                   183.597257   
cvm                                                          1.0   
cvmed                                                        0.0   
cvmode         0    0.0
Name: tier_trips_end_at

In [197]:
afternoon_nan_delay_tier = check_micromobility_datasets('tier', afternoon_nan_delay)

In [198]:
afternoon_nan_delay_tier.describe()

tier_trips_id          tier_trips_start_time  \
count   1.735000e+03                           1735   
mean    7.994897e+08  2023-07-15 13:52:46.167146752   
min     7.822646e+08            2023-07-01 15:05:00   
25%     7.823745e+08            2023-07-07 15:25:00   
50%     8.086423e+08            2023-07-14 15:45:00   
75%     8.087515e+08            2023-07-22 16:45:00   
max     8.323114e+08            2023-07-31 17:00:00   
std     1.650163e+07                            NaN   

                 tier_trips_end_time              trip_duration  \
count                           1735                       1735   
mean   2023-07-15 14:07:02.074928128  0 days 00:14:15.907780979   
min              2023-07-01 15:15:00            0 days 00:05:00   
25%              2023-07-07 15:40:00            0 days 00:10:00   
50%              2023-07-14 16:00:00            0 days 00:10:00   
75%              2023-07-22 17:00:00            0 days 00:15:00   
max              2023-07-31 18:20:00            0 days 01:55:00   
std                              NaN  0 days 00:09:56.508944721   

       trip_distance_kilometers  trip_distance_meters  start_stop_id  \
count               1735.000000           1735.000000    1289.000000   
mean                   1.734537           1734.536511    1323.040341   
min                    0.100253            100.252674      43.000000   
25%                    0.753111            753.111352     692.000000   
50%                    1.329632           1329.631893    1115.000000   
75%                    2.264472           2264.471964    1312.000000   
max                    8.717363           8717.363368    9703.000000   
std                    1.425133           1425.132719    1334.379586   

       end_stop_id  trip_duration_seconds  
count   885.000000            1735.000000  
mean   1368.688136             855.907781  
min      43.000000             300.000000  
25%    1102.000000             600.000000  
50%    1144.000000             600.000000  
75%    1240.000000             900.000000  
max    9703.000000            6900.000000  
std    1395.321414             596.508945

In [199]:
get_stats(afternoon_nan_delay_tier, ['trip_duration_seconds', 'trip_distance_kilometers'])

column                                     trip_duration_seconds  \
rows                                                        1735   
sum                                                    1485000.0   
mean                                                  855.907781   
median                                                     600.0   
mode           0    600.0
Name: trip_duration_seconds, dtype:...   
max                                                       6900.0   
min                                                        300.0   
std_dev                                               596.508945   
variance                                           355822.921133   
skewness                                                4.098347   
kurtosis                                               27.028733   
percentile_25                                              600.0   
percentile_75                                              900.0   
iqr                                                        300.0   
range                                                     6600.0   
cv                                                      0.696931   
qd                                                           0.2   
cs                                                      0.006871   
ck                                                      0.045312   
cvs                                                     0.006871   
cvk                                                     0.045312   
cvcs                                                    0.006871   
cvck                                                    0.045312   
cvcv                                                    0.696931   
cvqd                                                         0.2   
cvr                                                     7.711111   
cvm                                                          1.0   
cvmed                                                    0.70101   
cvmode         0    0.70101
Name: trip_duration_seconds, dtyp...   

column                                  trip_distance_kilometers  
rows                                                        1735  
sum                                                  3009.420847  
mean                                                    1.734537  
median                                                  1.329632  
mode           0       0.100253
1       0.100973
2       0.10...  
max                                                     8.717363  
min                                                     0.100253  
std_dev                                                 1.425133  
variance                                                2.031003  
skewness                                                1.721582  
kurtosis                                                3.658496  
percentile_25                                           0.753111  
percentile_75                                           2.264472  
iqr                                                     1.511361  
range                                                   8.617111  
cv                                                      0.821622  
qd                                                      0.500851  
cs                                                      1.208015  
ck                                                      2.567126  
cvs                                                     1.208015  
cvk                                                     2.567126  
cvcs                                                    1.208015  
cvck                                                    2.567126  
cvcv                                                    0.821622  
cvqd                                                    0.500851  
cvr                                                     4.967962  
cvm                                                          1.0  
cvmed                                                   0.766563  
cvmode         0

In [200]:
# get entries where trips start and end at station
afternoon_nan_delay_tier_station_station = afternoon_nan_delay_tier[afternoon_nan_delay_tier['end_stop_id'].notna() & afternoon_nan_delay_tier['start_stop_id'].notna()]
afternoon_nan_delay_tier_station_station

tier_trips_id tier_trips_start_time tier_trips_end_time vehicle type  \
3164081      782350087   2023-07-01 15:05:00 2023-07-01 15:15:00    e-scooter   
3177424      782361314   2023-07-01 15:10:00 2023-07-01 15:20:00    e-scooter   
3202018      782383767   2023-07-01 15:10:00 2023-07-01 15:20:00    e-scooter   
3237692      782416943   2023-07-01 15:10:00 2023-07-01 15:30:00    e-scooter   
3219195      782400097   2023-07-01 15:15:00 2023-07-01 15:45:00    e-scooter   
...                ...                   ...                 ...          ...   
3406811      832190220   2023-07-31 16:45:00 2023-07-31 17:00:00    e-scooter   
3325487      832124849   2023-07-31 16:45:00 2023-07-31 16:50:00    e-scooter   
3338340      832133612   2023-07-31 16:50:00 2023-07-31 17:00:00    e-scooter   
3305017      832110902   2023-07-31 17:00:00 2023-07-31 18:20:00    e-scooter   
3451042      832232640   2023-07-31 17:00:00 2023-07-31 17:10:00    e-scooter   

          trip_duration  trip_distance_kilometers  trip_distance_meters  \
3164081 0 days 00:10:00                  1.020358           1020.357721   
3177424 0 days 00:10:00                  1.006485           1006.484507   
3202018 0 days 00:10:00                  0.514913            514.913225   
3237692 0 days 00:20:00                  2.413493           2413.492560   
3219195 0 days 00:30:00                  4.263048           4263.048212   
...                 ...                       ...                   ...   
3406811 0 days 00:15:00                  3.037464           3037.463725   
3325487 0 days 00:05:00                  0.275064            275.063895   
3338340 0 days 00:10:00                  0.266824            266.823960   
3305017 0 days 01:20:00                  0.257841            257.841257   
3451042 0 days 00:10:00                  1.899790           1899.790483   

         start_stop_id                            start_stop_name  \
3164081         1162.0                              Bonn Rosental   
3177424         1522.0                                Bonn Vilich   
3202018         1110.0                         Bonn Wilhelmsplatz   
3237692         1172.0                            Bonn Bataverweg   
3219195         1513.0                      Bonn Rheindorfer Str.   
...                ...                                        ...   
3406811         1221.0                          Bonn Kaufmannstr.   
3325487         1523.0                        Bonn Vilich Kloster   
3338340         1115.0  Bonn Bertha-Von-Suttner-Pl./Beethovenhaus   
3305017          687.0                                   Bonn Hbf   
3451042         1514.0               Bonn Schwarzrheindorf Schule   

                                         start_buffer_zone  end_stop_id  \
3164081  801621     POLYGON ((7.157885983913106 50.7227...       1181.0   
3177424  801621     POLYGON ((7.157885983913106 50.7227...       1128.0   
3202018  801621     POLYGON ((7.157885983913106 50.7227...       1115.0   
3237692  801621     POLYGON ((7.157885983913106 50.7227...        687.0   
3219195  801621     POLYGON ((7.157885983913106 50.7227...       1268.0   
...                                                    ...          ...   
3406811  801621     POLYGON ((7.157885983913106 50.7227...        684.0   
3325487  801621     POLYGON ((7.157885983913106 50.7227...       1522.0   
3338340  801621     POLYGON ((7.157885983913106 50.7227...       2667.0   
3305017  801621     POLYGON ((7.157885983913106 50.7227...       1106.0   
3451042  801621     POLYGON ((7.157885983913106 50.7227...       1115.0   

                                     end_stop_name  \
3164081                           Bonn Am Nordpark   
3177424                            Bonn Gartenstr.   
3202018  Bonn Bertha-Von-Suttner-Pl./Beethovenhaus   
3237692                                   Bonn Hbf   
3219195                              Bonn Rheinaue   
...                                            ...   
3406811    Bonn Bundesrechn

In [201]:
afternoon_nan_delay_tier_station_station.describe()

tier_trips_id          tier_trips_start_time  \
count   7.690000e+02                            769   
mean    7.991622e+08  2023-07-15 05:50:23.407022080   
min     7.822652e+08            2023-07-01 15:05:00   
25%     7.823558e+08            2023-07-06 17:00:00   
50%     8.086398e+08            2023-07-13 16:15:00   
75%     8.087497e+08            2023-07-22 16:05:00   
max     8.323095e+08            2023-07-31 17:00:00   
std     1.681556e+07                            NaN   

                 tier_trips_end_time              trip_duration  \
count                            769                        769   
mean   2023-07-15 06:04:03.042913024  0 days 00:13:39.635890767   
min              2023-07-01 15:15:00            0 days 00:05:00   
25%              2023-07-06 17:15:00            0 days 00:10:00   
50%              2023-07-13 16:25:00            0 days 00:10:00   
75%              2023-07-22 16:25:00            0 days 00:15:00   
max              2023-07-31 18:20:00            0 days 01:55:00   
std                              NaN  0 days 00:10:10.150145935   

       trip_distance_kilometers  trip_distance_meters  start_stop_id  \
count                769.000000            769.000000     769.000000   
mean                   1.498532           1498.531722    1421.409623   
min                    0.100253            100.252674      43.000000   
25%                    0.643670            643.670142    1102.000000   
50%                    1.144710           1144.709662    1115.000000   
75%                    2.068049           2068.049076    1255.000000   
max                    8.717363           8717.363368    9703.000000   
std                    1.278897           1278.897298    1481.578742   

       end_stop_id  trip_duration_seconds  
count   769.000000             769.000000  
mean   1364.197659             819.635891  
min      43.000000             300.000000  
25%    1102.000000             600.000000  
50%    1144.000000             600.000000  
75%    1231.000000             900.000000  
max    9703.000000            6900.000000  
std    1342.822707             610.150146

In [202]:
# get statistics for the tier trips that start and end at a station
get_stats(afternoon_nan_delay_tier_station_station, ['trip_duration_seconds', 'trip_distance_kilometers'])

column                                     trip_duration_seconds  \
rows                                                         769   
sum                                                     630300.0   
mean                                                  819.635891   
median                                                     600.0   
mode           0    600.0
Name: trip_duration_seconds, dtype:...   
max                                                       6900.0   
min                                                        300.0   
std_dev                                               610.150146   
variance                                           372283.200585   
skewness                                                4.612098   
kurtosis                                               32.849508   
percentile_25                                              600.0   
percentile_75                                              900.0   
iqr                                                        300.0   
range                                                     6600.0   
cv                                                      0.744416   
qd                                                           0.2   
cs                                                      0.007559   
ck                                                      0.053838   
cvs                                                     0.007559   
cvk                                                     0.053838   
cvcs                                                    0.007559   
cvck                                                    0.053838   
cvcv                                                    0.744416   
cvqd                                                         0.2   
cvr                                                     8.052356   
cvm                                                          1.0   
cvmed                                                   0.732032   
cvmode         0    0.732032
Name: trip_duration_seconds, dty...   

column                                  trip_distance_kilometers  
rows                                                         769  
sum                                                  1152.370894  
mean                                                    1.498532  
median                                                   1.14471  
mode           0      0.100253
1      0.100973
2      0.10326...  
max                                                     8.717363  
min                                                     0.100253  
std_dev                                                 1.278897  
variance                                                1.635578  
skewness                                                2.093526  
kurtosis                                                6.542785  
percentile_25                                            0.64367  
percentile_75                                           2.068049  
iqr                                                     1.424379  
range                                                   8.617111  
cv                                                      0.853434  
qd                                                      0.525268  
cs                                                      1.636978  
ck                                                      5.115958  
cvs                                                     1.636978  
cvk                                                     5.115958  
cvcs                                                    1.636978  
cvck                                                    5.115958  
cvcv                                                    0.853434  
cvqd                                                    0.525268  
cvr                                                     5.750369  
cvm                                                          1.0  
cvmed                                                   0.763888  
cvmode         0

In [203]:
afternoon_nan_delay_next = check_micromobility_datasets('next', afternoon_nan_delay)

In [204]:
afternoon_nan_delay_next.describe()

nextbike_trips_id      nextbike_trips_start_time  \
count       4.686000e+03                           4686   
mean        3.793833e+07  2023-07-16 01:22:18.489116416   
min         3.771653e+07            2023-07-01 15:01:00   
25%         3.782648e+07            2023-07-07 16:11:00   
50%         3.794152e+07            2023-07-15 15:21:00   
75%         3.804853e+07            2023-07-24 15:11:00   
max         3.817169e+07            2023-07-31 17:01:00   
std         1.286068e+05                            NaN   

             nextbike_trips_end_time              trip_duration  \
count                           4686                       4686   
mean   2023-07-16 01:37:30.140845056  0 days 00:15:11.651728553   
min              2023-07-01 15:11:00            0 days 00:05:00   
25%              2023-07-07 16:26:00            0 days 00:10:00   
50%              2023-07-15 15:36:00            0 days 00:15:00   
75%              2023-07-24 15:26:00            0 days 00:18:45   
max              2023-07-31 17:16:00            0 days 02:00:00   
std                              NaN  0 days 00:10:09.481087896   

       trip_distance_kilometers  trip_distance_meters  start_stop_id  \
count               4686.000000           4686.000000    3743.000000   
mean                   1.765001           1765.000710    1161.844243   
min                    0.100177            100.177408      43.000000   
25%                    0.809857            809.857255     687.000000   
50%                    1.342536           1342.535874    1115.000000   
75%                    2.253821           2253.820538    1221.000000   
max                   11.879656          11879.655514    9780.000000   
std                    1.473333           1473.332501    1029.125263   

       end_stop_id  trip_duration_seconds  
count  2705.000000            4686.000000  
mean   1287.642884             911.651729  
min      43.000000             300.000000  
25%    1102.000000             600.000000  
50%    1150.000000             900.000000  
75%    1221.000000            1125.000000  
max    9703.000000            7200.000000  
std    1208.245403             609.481088

In [205]:
get_stats(afternoon_nan_delay_next, ['trip_duration_seconds', 'trip_distance_kilometers'])

column                                     trip_duration_seconds  \
rows                                                        4686   
sum                                                    4272000.0   
mean                                                  911.651729   
median                                                     900.0   
mode           0    600.0
Name: trip_duration_seconds, dtype:...   
max                                                       7200.0   
min                                                        300.0   
std_dev                                               609.481088   
variance                                           371467.196504   
skewness                                                3.849033   
kurtosis                                                25.08933   
percentile_25                                              600.0   
percentile_75                                             1125.0   
iqr                                                        525.0   
range                                                     6900.0   
cv                                                      0.668546   
qd                                                      0.304348   
cs                                                      0.006315   
ck                                                      0.041165   
cvs                                                     0.006315   
cvk                                                     0.041165   
cvcs                                                    0.006315   
cvck                                                    0.041165   
cvcv                                                    0.668546   
cvqd                                                    0.304348   
cvr                                                      7.56868   
cvm                                                          1.0   
cvmed                                                   0.987219   
cvmode         0    0.658146
Name: trip_duration_seconds, dty...   

column                                  trip_distance_kilometers  
rows                                                        4686  
sum                                                  8270.793325  
mean                                                    1.765001  
median                                                  1.342536  
mode           0    0.173610
1    1.355822
Name: trip_distanc...  
max                                                    11.879656  
min                                                     0.100177  
std_dev                                                 1.473333  
variance                                                2.170709  
skewness                                                2.183924  
kurtosis                                                7.095988  
percentile_25                                           0.809857  
percentile_75                                           2.253821  
iqr                                                     1.443963  
range                                                  11.779478  
cv                                                      0.834749  
qd                                                      0.471317  
cs                                                      1.482302  
ck                                                      4.816284  
cvs                                                     1.482302  
cvk                                                     4.816284  
cvcs                                                    1.482302  
cvck                                                    4.816284  
cvcv                                                    0.834749  
cvqd                                                    0.471317  
cvr                                                     6.673923  
cvm                                                          1.0  
cvmed                                                   0.760643  
cvmode         0

In [206]:
# get entries where trips start and end at station
afternoon_nan_delay_next_station_station = afternoon_nan_delay_next[afternoon_nan_delay_next['end_stop_id'].notna() & afternoon_nan_delay_next['start_stop_id'].notna()]
afternoon_nan_delay_next_station_station

nextbike_trips_id nextbike_trips_start_time nextbike_trips_end_time  \
1422827           38000437       2023-07-01 15:01:00     2023-07-01 15:11:00   
1267270           37827538       2023-07-01 15:06:00     2023-07-01 15:26:00   
1473154           37976991       2023-07-01 15:06:00     2023-07-01 15:21:00   
1367325           37936293       2023-07-01 15:16:00     2023-07-01 15:41:00   
1427340           38001424       2023-07-01 15:21:00     2023-07-01 15:36:00   
...                    ...                       ...                     ...   
1391497           37923983       2023-07-31 16:56:00     2023-07-31 17:06:00   
1531048           38082063       2023-07-31 16:56:00     2023-07-31 17:06:00   
1460547           38027186       2023-07-31 17:01:00     2023-07-31 17:16:00   
1638349           37769768       2023-07-31 17:01:00     2023-07-31 17:11:00   
1649035           37780454       2023-07-31 17:01:00     2023-07-31 17:11:00   

         nextbike_trips_start_at_station  nextbike_trips_end_at_station  \
1422827                             True                          False   
1267270                            False                          False   
1473154                            False                          False   
1367325                            False                          False   
1427340                            False                          False   
...                                  ...                            ...   
1391497                            False                          False   
1531048                            False                          False   
1460547                            False                          False   
1638349                            False                          False   
1649035                            False                          False   

        vehicle type   trip_duration  trip_distance_kilometers  \
1422827         bike 0 days 00:10:00                  0.950590   
1267270         bike 0 days 00:20:00                  1.863179   
1473154         bike 0 days 00:15:00                  1.698786   
1367325         bike 0 days 00:25:00                  5.727869   
1427340         bike 0 days 00:15:00                  1.652885   
...              ...             ...                       ...   
1391497         bike 0 days 00:10:00                  1.469302   
1531048         bike 0 days 00:10:00                  0.473075   
1460547         bike 0 days 00:15:00                  1.106455   
1638349         bike 0 days 00:10:00                  0.218677   
1649035         bike 0 days 00:10:00                  0.559276   

         trip_distance_meters  \
1422827            950.590405   
1267270           1863.178852   
1473154           1698.786039   
1367325           5727.869332   
1427340           1652.885159   
...                       ...   
1391497           1469.302141   
1531048            473.075103   
1460547           1106.455028   
1638349            218.676771   
1649035            559.275923   

                                            start_location  \
1422827  b'\x01\x01\x00\x00\x00\x06.\x8f5#c\x1c@\x9dJ\x...   
1267270  b"\x01\x01\x00\x00\x00c('\xdaUh\x1c@H\xfe`\xe0...   
1473154  b'\x01\x01\x00\x00\x00e\xaa`TRg\x1c@`=\xee[\xa...   
1367325  b'\x01\x01\x00\x00\x00\xe7U\x9d\xd5\x02[\x1c@\...   
1427340  b'\x01\x01\x00\x00\x00Ww,\xb6Ie\x1c@\xe4\xbdje...   
...                                                    ...   
1391497  b'\x01\x01\x00\x00\x00\x9b\xaf\x92\x8f\xddU\x1...   
1531048  b'\x01\x01\x00\x00\x00e\xe2VA\x0cd\x1c@\x96\xc...   
1460547  b'\x01\x01\x00\x00\x00h\xeau\x8b\xc0h\x1c@\xf5...   
1638349  b'\x01\x01\x00\x00\x00\xce\x8b\x13_\xedx\x1c@\...   
1649035  b'\x01\x01\x00\x00\x00m6Vb\x9ee\x1c@\x80\xf1\x...   

                                              end_location  start_stop_id  \
1422827  b'\x01\x01\x00\x00\x00\xf9\xa1\xd2\x88\x99]\x1...         1102.0   
1267270  b'\x01\x01\x00\x00\x00\xa0R%\xca\xdeb\x1c@_Cp\...

In [207]:
afternoon_nan_delay_next_station_station.describe()

nextbike_trips_id      nextbike_trips_start_time  \
count       2.313000e+03                           2313   
mean        3.793795e+07  2023-07-16 00:01:35.149156864   
min         3.771653e+07            2023-07-01 15:01:00   
25%         3.782048e+07            2023-07-07 16:11:00   
50%         3.794164e+07            2023-07-14 16:56:00   
75%         3.804974e+07            2023-07-23 16:56:00   
max         3.817169e+07            2023-07-31 17:01:00   
std         1.298853e+05                            NaN   

             nextbike_trips_end_time              trip_duration  \
count                           2313                       2313   
mean   2023-07-16 00:15:43.268482560  0 days 00:14:08.119325551   
min              2023-07-01 15:11:00            0 days 00:05:00   
25%              2023-07-07 16:26:00            0 days 00:10:00   
50%              2023-07-14 17:06:00            0 days 00:10:00   
75%              2023-07-23 17:11:00            0 days 00:15:00   
max              2023-07-31 17:16:00            0 days 02:00:00   
std                              NaN  0 days 00:09:49.357135789   

       trip_distance_kilometers  trip_distance_meters  start_stop_id  \
count               2313.000000           2313.000000    2313.000000   
mean                   1.454157           1454.156901    1193.006053   
min                    0.100177            100.177408      43.000000   
25%                    0.743084            743.083512     687.000000   
50%                    1.174426           1174.426429    1115.000000   
75%                    1.847798           1847.797747    1184.000000   
max                    8.255968           8255.968494    9780.000000   
std                    1.115475           1115.475190    1069.002756   

       end_stop_id  trip_duration_seconds  
count  2313.000000            2313.000000  
mean   1314.226113             848.119326  
min      43.000000             300.000000  
25%    1103.000000             600.000000  
50%    1151.000000             600.000000  
75%    1221.000000             900.000000  
max    9703.000000            7200.000000  
std    1231.623478             589.357136

In [208]:
# get statistics for the tier trips that start and end at a station
get_stats(afternoon_nan_delay_next_station_station, ['trip_duration_seconds', 'trip_distance_kilometers'])

column                                     trip_duration_seconds  \
rows                                                        2313   
sum                                                    1961700.0   
mean                                                  848.119326   
median                                                     600.0   
mode           0    600.0
Name: trip_duration_seconds, dtype:...   
max                                                       7200.0   
min                                                        300.0   
std_dev                                               589.357136   
variance                                           347341.833506   
skewness                                                4.536452   
kurtosis                                               32.524953   
percentile_25                                              600.0   
percentile_75                                              900.0   
iqr                                                        300.0   
range                                                     6900.0   
cv                                                      0.694899   
qd                                                           0.2   
cs                                                      0.007697   
ck                                                      0.055187   
cvs                                                     0.007697   
cvk                                                     0.055187   
cvcs                                                    0.007697   
cvck                                                    0.055187   
cvcv                                                    0.694899   
cvqd                                                         0.2   
cvr                                                     8.135648   
cvm                                                          1.0   
cvmed                                                   0.707448   
cvmode         0    0.707448
Name: trip_duration_seconds, dty...   

column                                  trip_distance_kilometers  
rows                                                        2313  
sum                                                  3363.464913  
mean                                                    1.454157  
median                                                  1.174426  
mode           0    1.355822
Name: trip_distance_kilometers, ...  
max                                                     8.255968  
min                                                     0.100177  
std_dev                                                 1.115475  
variance                                                1.244285  
skewness                                                2.023467  
kurtosis                                                5.759467  
percentile_25                                           0.743084  
percentile_75                                           1.847798  
iqr                                                     1.104714  
range                                                   8.155791  
cv                                                      0.767094  
qd                                                      0.426386  
cs                                                      1.813995  
ck                                                      5.163241  
cvs                                                     1.813995  
cvk                                                     5.163241  
cvcs                                                    1.813995  
cvck                                                    5.163241  
cvcv                                                    0.767094  
cvqd                                                    0.426386  
cvr                                                     5.608605  
cvm                                                          1.0  
cvmed                                                   0.807634  
cvmode         0

In [209]:
afternoon_delay.describe()

route_id      agency_id     route_type     service_id  \
count  110777.000000  110777.000000  110777.000000  110777.000000   
mean      566.915912       6.007258       2.767452    2740.395452   
min        60.000000       6.000000       0.000000      43.000000   
25%       602.000000       6.000000       3.000000      64.000000   
50%       608.000000       6.000000       3.000000      64.000000   
75%       611.000000       6.000000       3.000000     130.000000   
max       843.000000      12.000000       3.000000   27690.000000   
std       148.887082       0.203825       0.802229    8006.513541   

        direction_id       shape_id        stop_id  \
count  110777.000000  110777.000000  110777.000000   
mean        0.515062    3588.295124    2291.743178   
min         0.000000       6.000000      43.000000   
25%         0.000000    1915.000000    1214.000000   
50%         1.000000    2717.000000    1433.000000   
75%         1.000000    5633.000000    1673.000000   
max         1.000000   10365.000000    9780.000000   
std         0.499775    2820.002051    2380.454528   

                 actual_arrival_time          actual_departure_time  \
count                         107857                         110777   
mean   2023-07-16 16:57:17.498308096  2023-07-16 17:38:26.224577536   
min              2023-07-01 15:00:00            2023-07-01 15:00:15   
25%              2023-07-09 15:15:00            2023-07-09 15:16:30   
50%              2023-07-17 15:45:00            2023-07-17 15:49:45   
75%              2023-07-23 16:56:15            2023-07-24 15:02:30   
max              2023-07-31 17:11:45            2023-07-31 17:12:00   
std                              NaN                            NaN   

       vrs_timestamp  ...  departure_delay_float actual_arrival_time_float  \
count  110777.000000  ...          110777.000000             110777.000000   
mean   153118.342824  ...               0.644719             153833.479287   
min    130304.000000  ...               0.166667                  0.000000   
25%    141804.000000  ...               0.250000             152715.000000   
50%    144806.000000  ...               0.500000             155830.000000   
75%    152306.000000  ...               0.750000             162900.000000   
max    222305.000000  ...              24.000000             171145.000000   
std     24133.310663  ...               1.141496              25845.055813   

      actual_departure_time_float arrival_delay_span    weather_int  \
count               110777.000000           110777.0  110777.000000   
mean                158040.192459                0.0       0.163175   
min                 150010.000000                0.0       0.000000   
25%                 153030.000000                0.0       0.000000   
50%                 160045.000000                0.0       0.000000   
75%                 163015.000000                0.0       0.000000   
max                 171200.000000                0.0       2.000000   
std                   5296.006305                0.0       0.408688   

       time_span_int_arrival        weekend  time_span_int  delay_category  \
count          110777.000000  110777.000000  110777.000000   110777.000000   
mean                3.895466       0.733275       4.001950        0.645621   
min                 0.000000       0.000000       4.000000       -1.000000   
25%                 4.000000       0.000000       4.000000        0.000000   
50%                 4.000000       0.000000       4.000000        1.000000   
75%                 4.000000       2.000000       4.000000        1.000000   
max                 5.000000       3.000000       5.000000        1.000000   
std                 0.642110       1.037805       0.044114        0.530580   

       cancelled_trip  
count        110777.0  
mean              0.0  
min               0.0  
25%               0.0  
50%               0.0  
75%               0.0  
max               0.0  
std               0.0  



In [210]:
afternoon_no_delay.describe()

route_id     agency_id    route_type    service_id  direction_id  \
count  67154.000000  67154.000000  67154.000000  67154.000000  67154.000000   
mean     571.863463      7.051434      2.660795   5437.591149      0.514638   
min       16.000000      1.000000      0.000000     43.000000      0.000000   
25%      600.000000      6.000000      3.000000     64.000000      0.000000   
50%      607.000000      6.000000      3.000000     64.000000      1.000000   
75%      630.000000      8.000000      3.000000    151.000000      1.000000   
max      884.000000     12.000000      3.000000  29144.000000      1.000000   
std      206.560708      2.143687      0.950037  10826.854399      0.499789   

           shape_id       stop_id            actual_arrival_time  \
count  67154.000000  67154.000000                          48321   
mean    4224.582795   2259.250588  2023-07-16 15:16:11.000186368   
min        6.000000     43.000000            2023-07-01 14:59:00   
25%     2021.000000   1182.000000            2023-07-08 16:55:30   
50%     3858.000000   1433.000000            2023-07-17 15:49:00   
75%     6377.000000   1714.000000            2023-07-23 16:31:40   
max    10365.000000   9780.000000            2023-07-31 16:59:00   
std     2858.957917   2386.316942                            NaN   

               actual_departure_time  vrs_timestamp  ...  \
count                          67154   67154.000000  ...   
mean   2023-07-16 16:18:48.688759808  152664.441910  ...   
min              2023-07-01 15:00:00  130304.000000  ...   
25%              2023-07-08 16:57:00  141804.000000  ...   
50%              2023-07-17 15:43:00  144806.000000  ...   
75%              2023-07-23 16:59:00  152306.000000  ...   
max              2023-07-31 17:10:15  222305.000000  ...   
std                              NaN   23391.237362  ...   

       departure_delay_float actual_arrival_time_float  \
count           67154.000000              67154.000000   
mean                0.038707             113618.312833   
min                 0.000000                  0.000000   
25%                 0.000000                  0.000000   
50%                 0.000000             153645.000000   
75%                 0.000000             161800.000000   
max                24.000000             170200.000000   
std                 0.386616              71077.028162   

      actual_departure_time_float arrival_delay_span   weather_int  \
count                67154.000000            67154.0  67154.000000   
mean                158028.174122                0.0      0.167287   
min                 150000.000000                0.0      0.000000   
25%                 153000.000000                0.0      0.000000   
50%                 160000.000000                0.0      0.000000   
75%                 163000.000000                0.0      0.000000   
max                 171200.000000                0.0      2.000000   
std                   5307.310643                0.0      0.416706   

       time_span_int_arrival       weekend  time_span_int  delay_category  \
count           67154.000000  67154.000000   67154.000000    67154.000000   
mean                2.872785      0.750648       4.000566       -0.273282   
min                 0.000000      0.000000       4.000000       -1.000000   
25%                 0.000000      0.000000       4.000000       -1.000000   
50%                 4.000000      0.000000       4.000000        0.000000   
75%                 4.000000      2.000000       4.000000        0.000000   
max                 5.000000      3.000000       5.000000        1.000000   
std                 1.794998      1.038617       0.023781        0.461441   

       cancelled_trip  
count         67154.0  
mean              0.0  
min               0.0  
25%               0.0  
50%               0.0  
75%               0.0  
max               0.0  
std               0.0  

[8 rows x 38 columns]

In [211]:
afternoon_nan_delay.describe()

route_id      agency_id     route_type     service_id  \
count  127187.000000  127187.000000  127187.000000  127187.000000   
mean      558.853389       6.345719       2.689143    3987.328029   
min        16.000000       1.000000       0.000000      43.000000   
25%       601.000000       6.000000       3.000000      64.000000   
50%       607.000000       6.000000       3.000000      64.000000   
75%       614.000000       6.000000       3.000000     130.000000   
max       884.000000      12.000000       3.000000   29145.000000   
std       179.563157       1.282154       0.914301    9473.720335   

        direction_id       shape_id        stop_id actual_arrival_time  \
count  127187.000000  127187.000000  127187.000000                   0   
mean        0.490247    4067.026080    2260.845409                 NaT   
min         0.000000       6.000000      43.000000                 NaT   
25%         0.000000    1945.000000    1223.000000                 NaT   
50%         0.000000    2936.000000    1467.000000                 NaT   
75%         1.000000    6327.000000    1684.000000                 NaT   
max         1.000000   10365.000000    9780.000000                 NaT   
std         0.499907    2939.914685    2339.854372                 NaN   

      actual_departure_time  vrs_timestamp  ...  departure_delay_float  \
count                     0  127187.000000  ...                    0.0   
mean                    NaT  146195.516515  ...                    NaN   
min                     NaT  102304.000000  ...                    NaN   
25%                     NaT  140805.000000  ...                    NaN   
50%                     NaT  144304.000000  ...                    NaN   
75%                     NaT  151305.000000  ...                    NaN   
max                     NaT  222305.000000  ...                    NaN   
std                     NaN   12874.688083  ...                    NaN   

      actual_arrival_time_float actual_departure_time_float  \
count                  127187.0                    127187.0   
mean                        0.0                         0.0   
min                         0.0                         0.0   
25%                         0.0                         0.0   
50%                         0.0                         0.0   
75%                         0.0                         0.0   
max                         0.0                         0.0   
std                         0.0                         0.0   

      arrival_delay_span    weather_int  time_span_int_arrival        weekend  \
count           127187.0  127187.000000               127187.0  127187.000000   
mean                 0.0       0.218867                    0.0       0.716284   
min                  0.0       0.000000                    0.0       0.000000   
25%                  0.0       0.000000                    0.0       0.000000   
50%                  0.0       0.000000                    0.0       0.000000   
75%                  0.0       0.000000                    0.0       1.000000   
max                  0.0       2.000000                    0.0       3.000000   
std                  0.0       0.463065                    0.0       0.980295   

       time_span_int  delay_category  cancelled_trip  
count       127187.0        127187.0        127187.0  
mean             0.0            -1.0             1.0  
min              0.0            -1.0             1.0  
25%              0.0            -1.0             1.0  
50%              0.0            -1.0             1.0  
75%              0.0            -1.0             1.0  
max              0.0            -1.0             1.0  
std              0.0             0.0             0.0  

[8 rows x 38 columns]

#### Evening Rush Time

In [212]:
evening_rush_delay = delay[(delay['scheduled_arrival_time'].dt.hour >= 17) & (delay['scheduled_arrival_time'].dt.hour <= 19)]
evening_rush_delay

route_id  agency_id route_short_name  route_type route_type_name  \
54784         606          6              606           3             Bus   
54791         637          6              637           3             Bus   
54803         603          6              603           3             Bus   
54804         608          6              608           3             Bus   
54805         611          6              611           3             Bus   
...           ...        ...              ...         ...             ...   
2549892       633          6              633           3             Bus   
2549893       607          6              607           3             Bus   
2549897       604          6              604           3             Bus   
2549898       608          6              608           3             Bus   
2549900       600          6              600           3             Bus   

                               agency_name  service_id  \
54784    SWB Stadtwerke Bonn Verkehrs GmbH         130   
54791    SWB Stadtwerke Bonn Verkehrs GmbH         130   
54803    SWB Stadtwerke Bonn Verkehrs GmbH         130   
54804    SWB Stadtwerke Bonn Verkehrs GmbH         130   
54805    SWB Stadtwerke Bonn Verkehrs GmbH         130   
...                                    ...         ...   
2549892  SWB Stadtwerke Bonn Verkehrs GmbH          64   
2549893  SWB Stadtwerke Bonn Verkehrs GmbH          43   
2549897  SWB Stadtwerke Bonn Verkehrs GmbH          64   
2549898  SWB Stadtwerke Bonn Verkehrs GmbH          64   
2549900  SWB Stadtwerke Bonn Verkehrs GmbH          64   

                                                   trip_id  \
54784    6060195-606-006-1357.2.21:164100-42-1_408CE4FB...   
54791    6370121-637-006-7184.2.23:164900-17-1_A8ED8796...   
54803    6030372-603-006-2304.2.22:165100-41-1_788E386E...   
54804    6080182-608-006-1574.2.24:160900-47-1_5452CA2B...   
54805    6110205-611-006-1723.2.21:162600-60-1_0618031A...   
...                                                    ...   
2549892  6330062-633-006-1584.2.24:194300-24-1_D28C05E2...   
2549893  6070070-607-006-1584.2.22:192300-46-1_3D1B0B48...   
2549897  6040103-604-006-1382.2.21:195700-49-1_E62D4CCA...   
2549898  6080117-608-006-1374.2.21:192100-46-1_F091AAE0...   
2549900  6000088-600-006-8813.2.22:195900-32-1_E8E14017...   

                         trip_headsign  direction_id  ...  delay_span  \
54784                       Ramersdorf             0  ...         0-5   
54791    Bad Godesberg Bf / Rheinallee             0  ...         0-5   
54803                 Röttgen Schleife             1  ...         0-5   
54804               Hardthöhe/Südwache             1  ...         0-5   
54805             Lessenich Sportplatz             0  ...         0-5   
...                                ...           ...  ...         ...   
2549892               Endenich Nord Bf             1  ...         0-5   
2549893             Hardtberg Klinikum             1  ...         0-5   
2549897                         Hersel             0  ...         0-5   
2549898                        Gielgen             0  ...         0-5   
2549900            Ippendorf Altenheim             1  ...         0-5   

         arrival_delay_span weather_int time_span_arrival  \
54784                     0           0      evening rush   
54791                     0           0      evening rush   
54803                     0           0      evening rush   
54804                     0           0      evening rush   
54805                     0           0      evening rush   
...                     ...         ...               ...   
2549892                   0           1                 0   
2549893                   0           1      evening rush   
2549897                   0           1      evening rush   
2549898                   0           1                 0   
2549900                   0           1      evening rush   

         time_span_int_arrival  

In [213]:
get_stats(evening_rush_delay, ['tier_trips_count', 'tier_trips_end_at_station_count', 'nextbike_trips_count', 'nextbike_trips_end_at_station_count', 'current_temp', 'current_precipitation_volume'])

/tmp/ipykernel_2575952/41814695.py:51: RuntimeWarning: invalid value encountered in scalar divide
  qd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:55: RuntimeWarning: invalid value encountered in scalar divide
  cvqd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:51: RuntimeWarning: invalid value encountered in scalar divide
  qd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:55: RuntimeWarning: invalid value encountered in scalar divide
  cvqd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:51: RuntimeWarning: invalid value encountered in scalar divide
  qd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:55: RuntimeWarning: invalid value encountered in scalar divide
  cvqd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:51: RuntimeWarning: invalid value encountered in scalar divide
  qd = iqr / (percentile_75 + percenti

column                                        tier_trips_count  \
rows                                                    173541   
sum                                                       2557   
mean                                                  0.014734   
median                                                     0.0   
mode               0    0
Name: tier_trips_count, dtype: int64   
max                                                          6   
min                                                          0   
std_dev                                               0.132817   
variance                                               0.01764   
skewness                                             10.809661   
kurtosis                                              156.8474   
percentile_25                                              0.0   
percentile_75                                              0.0   
iqr                                                        0.0   
range                                                        6   
cv                                                    9.014181   
qd                                                         NaN   
cs                                                     81.3874   
ck                                                 1180.925334   
cvs                                                    81.3874   
cvk                                                1180.925334   
cvcs                                                   81.3874   
cvck                                               1180.925334   
cvcv                                                  9.014181   
cvqd                                                       NaN   
cvr                                                 407.213923   
cvm                                                        1.0   
cvmed                                                      0.0   
cvmode         0    0.0
Name: tier_trips_count, dtype: float64   

column                           tier_trips_end_at_station_count  \
rows                                                      173541   
sum                                                         2058   
mean                                                    0.011859   
median                                                       0.0   
mode           0    0
Name: tier_trips_end_at_station_count, ...   
max                                                            4   
min                                                            0   
std_dev                                                  0.11842   
variance                                                0.014023   
skewness                                               11.732608   
kurtosis                                              175.034516   
percentile_25                                                0.0   
percentile_75                                                0.0   
iqr                                                          0.0   
range                                                          4   
cv                                                      9.985758   
qd                                                           NaN   
cs                                                     99.076408   
ck                                                   1478.084936   
cvs                                                    99.076408   
cvk                                                  1478.084936   
cvcs                                                   99.076408   
cvck                                                 1478.084936   
cvcv                                                    9.985758   
cvqd                                                         NaN   
cvr                                                   337.300292   
cvm                                                          1.0   
cvmed                                                        0.0   
cvmode         0    0.0
Name: tier_trips_end_at

In [214]:
evening_rush_delay_tier = check_micromobility_datasets('tier', evening_rush_delay)

In [215]:
evening_rush_delay_tier.describe()

tier_trips_id          tier_trips_start_time  \
count   1.777000e+03                           1777   
mean    7.991306e+08  2023-07-15 18:42:31.097355008   
min     7.822652e+08            2023-07-01 17:05:00   
25%     7.823795e+08            2023-07-07 19:55:00   
50%     8.086300e+08            2023-07-13 19:30:00   
75%     8.087496e+08            2023-07-22 18:35:00   
max     8.323141e+08            2023-07-31 19:45:00   
std     1.722181e+07                            NaN   

                 tier_trips_end_time              trip_duration  \
count                           1777                       1777   
mean   2023-07-15 18:56:37.580191232  0 days 00:14:06.482836240   
min              2023-07-01 17:15:00            0 days 00:05:00   
25%              2023-07-07 20:10:00            0 days 00:10:00   
50%              2023-07-13 19:50:00            0 days 00:10:00   
75%              2023-07-22 18:55:00            0 days 00:15:00   
max              2023-07-31 20:00:00            0 days 01:40:00   
std                              NaN  0 days 00:09:37.730745274   

       trip_distance_kilometers  trip_distance_meters  start_stop_id  \
count               1777.000000           1777.000000    1181.000000   
mean                   1.678474           1678.474229    1413.616427   
min                    0.101703            101.702520      43.000000   
25%                    0.689931            689.930766    1102.000000   
50%                    1.264383           1264.383400    1131.000000   
75%                    2.189167           2189.167219    1241.000000   
max                   11.565806          11565.805864    9703.000000   
std                    1.455883           1455.883189    1411.752050   

       end_stop_id  trip_duration_seconds  
count   878.000000            1777.000000  
mean   1467.892938             846.482836  
min      43.000000             300.000000  
25%    1106.000000             600.000000  
50%    1152.000000             600.000000  
75%    1245.000000             900.000000  
max    9703.000000            6000.000000  
std    1539.497012             577.730745

In [216]:
get_stats(evening_rush_delay_tier, ['trip_duration_seconds', 'trip_distance_kilometers'])

column                                     trip_duration_seconds  \
rows                                                        1777   
sum                                                    1504200.0   
mean                                                  846.482836   
median                                                     600.0   
mode           0    600.0
Name: trip_duration_seconds, dtype:...   
max                                                       6000.0   
min                                                        300.0   
std_dev                                               577.730745   
variance                                           333772.814035   
skewness                                                3.566142   
kurtosis                                               20.580482   
percentile_25                                              600.0   
percentile_75                                              900.0   
iqr                                                        300.0   
range                                                     5700.0   
cv                                                      0.682507   
qd                                                           0.2   
cs                                                      0.006173   
ck                                                      0.035623   
cvs                                                     0.006173   
cvk                                                     0.035623   
cvcs                                                    0.006173   
cvck                                                    0.035623   
cvcv                                                    0.682507   
cvqd                                                         0.2   
cvr                                                     6.733746   
cvm                                                          1.0   
cvmed                                                   0.708815   
cvmode         0    0.708815
Name: trip_duration_seconds, dty...   

column                                  trip_distance_kilometers  
rows                                                        1777  
sum                                                  2982.648705  
mean                                                    1.678474  
median                                                  1.264383  
mode           0        0.101703
1        0.101712
2        0...  
max                                                    11.565806  
min                                                     0.101703  
std_dev                                                 1.455883  
variance                                                2.119596  
skewness                                                2.060503  
kurtosis                                                6.072552  
percentile_25                                           0.689931  
percentile_75                                           2.189167  
iqr                                                     1.499236  
range                                                  11.464103  
cv                                                      0.867385  
qd                                                      0.520731  
cs                                                      1.415294  
ck                                                      4.171043  
cvs                                                     1.415294  
cvk                                                     4.171043  
cvcs                                                    1.415294  
cvck                                                    4.171043  
cvcv                                                    0.867385  
cvqd                                                    0.520731  
cvr                                                     6.830074  
cvm                                                          1.0  
cvmed                                                   0.753293  
cvmode         0

In [217]:
# get entries where trips start and end at station
evening_rush_delay_tier_station_station = evening_rush_delay_tier[evening_rush_delay_tier['end_stop_id'].notna() & evening_rush_delay_tier['start_stop_id'].notna()]
evening_rush_delay_tier_station_station

tier_trips_id tier_trips_start_time tier_trips_end_time vehicle type  \
3035496      782304577   2023-07-01 17:10:00 2023-07-01 17:20:00    e-scooter   
2954000      782279912   2023-07-01 17:15:00 2023-07-01 17:25:00    e-scooter   
3160534      782347810   2023-07-01 17:30:00 2023-07-01 17:35:00    e-scooter   
3165488      782351010   2023-07-01 17:30:00 2023-07-01 17:40:00    e-scooter   
3235072      782414557   2023-07-01 17:30:00 2023-07-01 17:40:00    e-scooter   
...                ...                   ...                 ...          ...   
3338358      832133621   2023-07-31 19:15:00 2023-07-31 19:20:00    e-scooter   
3481514      832261887   2023-07-31 19:15:00 2023-07-31 19:25:00    e-scooter   
3486988      832267143   2023-07-31 19:15:00 2023-07-31 19:30:00    e-scooter   
3485590      832265811   2023-07-31 19:25:00 2023-07-31 19:30:00    e-scooter   
3402440      832186033   2023-07-31 19:45:00 2023-07-31 20:00:00    e-scooter   

          trip_duration  trip_distance_kilometers  trip_distance_meters  \
3035496 0 days 00:10:00                  1.576509           1576.508878   
2954000 0 days 00:10:00                  1.327481           1327.480919   
3160534 0 days 00:05:00                  0.409722            409.722289   
3165488 0 days 00:10:00                  0.761879            761.879472   
3235072 0 days 00:10:00                  0.746957            746.957378   
...                 ...                       ...                   ...   
3338358 0 days 00:05:00                  0.146650            146.650179   
3481514 0 days 00:10:00                  1.046279           1046.278932   
3486988 0 days 00:15:00                  1.321194           1321.193806   
3485590 0 days 00:05:00                  0.212159            212.159418   
3402440 0 days 00:15:00                  0.621047            621.046655   

         start_stop_id                            start_stop_name  \
3035496         1102.0                         Bonn Friedensplatz   
2954000         1104.0                             Bonn Stadthaus   
3160534         1405.0                          Bonn Nordfriedhof   
3165488         1106.0                      Bonn Thomas-Mann-Str.   
3235072         1106.0                      Bonn Thomas-Mann-Str.   
...                ...                                        ...   
3338358         2667.0  Bonn Brüdergasse/Bertha-Von-Suttner-Platz   
3481514         1502.0                 Bonn Beueler Bahnhofsplatz   
3486988         1502.0                 Bonn Beueler Bahnhofsplatz   
3485590         1103.0                                 Bonn Markt   
3402440         1501.0                         Bonn Beuel Rathaus   

                                         start_buffer_zone  end_stop_id  \
3035496  801621     POLYGON ((7.157885983913106 50.7227...       1192.0   
2954000  801621     POLYGON ((7.157885983913106 50.7227...        688.0   
3160534  801621     POLYGON ((7.157885983913106 50.7227...       2738.0   
3165488  801621     POLYGON ((7.157885983913106 50.7227...       1115.0   
3235072  801621     POLYGON ((7.157885983913106 50.7227...       1115.0   
...                                                    ...          ...   
3338358  801621     POLYGON ((7.157885983913106 50.7227...       1103.0   
3481514  801621     POLYGON ((7.157885983913106 50.7227...       1958.0   
3486988  801621     POLYGON ((7.157885983913106 50.7227...       1045.0   
3485590  801621     POLYGON ((7.157885983913106 50.7227...        686.0   
3402440  801621     POLYGON ((7.157885983913106 50.7227...       1502.0   

                                     end_stop_name  \
3035496                             Bonn Ellerstr.   
2954000                                  Bonn West   
3160534                          Bonn Hedwigschule   
3165488  Bonn Bertha-Von-Suttner-Pl./Beethovenhaus   
3235072  Bonn Bertha-Von-Suttner-Pl./Beethovenhaus   
...                                            ...   
3338358                    

In [218]:
evening_rush_delay_tier_station_station.describe()

tier_trips_id          tier_trips_start_time  \
count   7.110000e+02                            711   
mean    7.976857e+08  2023-07-15 02:50:20.253164800   
min     7.822652e+08            2023-07-01 17:10:00   
25%     7.823561e+08            2023-07-07 19:22:30   
50%     7.824547e+08            2023-07-12 19:20:00   
75%     8.087315e+08            2023-07-21 19:15:00   
max     8.323115e+08            2023-07-31 19:45:00   
std     1.730912e+07                            NaN   

                 tier_trips_end_time              trip_duration  \
count                            711                        711   
mean   2023-07-15 03:03:01.856540160  0 days 00:12:41.603375527   
min              2023-07-01 17:20:00            0 days 00:05:00   
25%              2023-07-07 19:37:30            0 days 00:10:00   
50%              2023-07-12 19:30:00            0 days 00:10:00   
75%              2023-07-21 19:25:00            0 days 00:15:00   
max              2023-07-31 20:00:00            0 days 01:25:00   
std                              NaN  0 days 00:08:32.823957593   

       trip_distance_kilometers  trip_distance_meters  start_stop_id  \
count                711.000000            711.000000     711.000000   
mean                   1.342197           1342.197398    1397.776371   
min                    0.101703            101.702520      43.000000   
25%                    0.612077            612.076647    1103.000000   
50%                    1.046279           1046.278932    1131.000000   
75%                    1.726079           1726.078777    1234.500000   
max                    8.442163           8442.163487    9703.000000   
std                    1.118692           1118.692028    1372.319786   

       end_stop_id  trip_duration_seconds  
count   711.000000             711.000000  
mean   1526.603376             761.603376  
min      43.000000             300.000000  
25%    1110.000000             600.000000  
50%    1153.000000             600.000000  
75%    1244.500000             900.000000  
max    9703.000000            5100.000000  
std    1621.943005             512.823958

In [219]:
# get statistics for the tier trips that start and end at a station
get_stats(evening_rush_delay_tier_station_station, ['trip_duration_seconds', 'trip_distance_kilometers'])

column                                     trip_duration_seconds  \
rows                                                         711   
sum                                                     541500.0   
mean                                                  761.603376   
median                                                     600.0   
mode           0    600.0
Name: trip_duration_seconds, dtype:...   
max                                                       5100.0   
min                                                        300.0   
std_dev                                               512.823958   
variance                                           262988.411482   
skewness                                                4.018385   
kurtosis                                               25.150417   
percentile_25                                              600.0   
percentile_75                                              900.0   
iqr                                                        300.0   
range                                                     4800.0   
cv                                                      0.673348   
qd                                                           0.2   
cs                                                      0.007836   
ck                                                      0.049043   
cvs                                                     0.007836   
cvk                                                     0.049043   
cvcs                                                    0.007836   
cvck                                                    0.049043   
cvcv                                                    0.673348   
cvqd                                                         0.2   
cvr                                                     6.302493   
cvm                                                          1.0   
cvmed                                                   0.787812   
cvmode         0    0.787812
Name: trip_duration_seconds, dty...   

column                                  trip_distance_kilometers  
rows                                                         711  
sum                                                    954.30235  
mean                                                    1.342197  
median                                                  1.046279  
mode           0      0.101703
1      0.101712
2      0.10462...  
max                                                     8.442163  
min                                                     0.101703  
std_dev                                                 1.118692  
variance                                                1.251472  
skewness                                                1.928201  
kurtosis                                                5.277803  
percentile_25                                           0.612077  
percentile_75                                           1.726079  
iqr                                                     1.114002  
range                                                   8.340461  
cv                                                      0.833478  
qd                                                      0.476445  
cs                                                      1.723621  
ck                                                      4.717834  
cvs                                                     1.723621  
cvk                                                     4.717834  
cvcs                                                    1.723621  
cvck                                                    4.717834  
cvcv                                                    0.833478  
cvqd                                                    0.476445  
cvr                                                     6.214035  
cvm                                                          1.0  
cvmed                                                   0.779527  
cvmode         0

In [220]:
evening_rush_delay_next = check_micromobility_datasets('next', evening_rush_delay)

In [221]:
evening_rush_delay_next.describe()

nextbike_trips_id      nextbike_trips_start_time  \
count       4.482000e+03                           4482   
mean        3.793903e+07  2023-07-15 23:27:24.605086720   
min         3.771661e+07            2023-07-01 17:01:00   
25%         3.782629e+07            2023-07-08 18:42:15   
50%         3.794076e+07            2023-07-14 19:51:00   
75%         3.804970e+07            2023-07-22 17:36:00   
max         3.817174e+07            2023-07-31 20:01:00   
std         1.283549e+05                            NaN   

             nextbike_trips_end_time              trip_duration  \
count                           4482                       4482   
mean   2023-07-15 23:42:25.943774976  0 days 00:15:01.338688085   
min              2023-07-01 17:16:00            0 days 00:05:00   
25%              2023-07-08 18:56:00            0 days 00:10:00   
50%              2023-07-14 20:06:00            0 days 00:15:00   
75%              2023-07-22 17:46:00            0 days 00:20:00   
max              2023-07-31 20:11:00            0 days 01:55:00   
std                              NaN  0 days 00:09:38.768125936   

       trip_distance_kilometers  trip_distance_meters  start_stop_id  \
count               4482.000000           4482.000000    3189.000000   
mean                   1.690165           1690.164881    1350.659768   
min                    0.100057            100.057033      43.000000   
25%                    0.744561            744.560957    1103.000000   
50%                    1.313010           1313.010017    1145.000000   
75%                    2.209071           2209.070869    1224.000000   
max                   12.128969          12128.968591    9780.000000   
std                    1.385630           1385.629918    1302.501916   

       end_stop_id  trip_duration_seconds  
count  2445.000000            4482.000000  
mean   1371.394274             901.338688  
min      43.000000             300.000000  
25%    1104.000000             600.000000  
50%    1153.000000             900.000000  
75%    1224.000000            1200.000000  
max    9780.000000            6900.000000  
std    1352.892939             578.768126

In [222]:
get_stats(evening_rush_delay_next, ['trip_duration_seconds', 'trip_distance_kilometers'])

column                                     trip_duration_seconds  \
rows                                                        4482   
sum                                                    4039800.0   
mean                                                  901.338688   
median                                                     900.0   
mode           0    600.0
Name: trip_duration_seconds, dtype:...   
max                                                       6900.0   
min                                                        300.0   
std_dev                                               578.768126   
variance                                             334972.5436   
skewness                                                3.436843   
kurtosis                                               20.849667   
percentile_25                                              600.0   
percentile_75                                             1200.0   
iqr                                                        600.0   
range                                                     6600.0   
cv                                                      0.642121   
qd                                                      0.333333   
cs                                                      0.005938   
ck                                                      0.036024   
cvs                                                     0.005938   
cvk                                                     0.036024   
cvcs                                                    0.005938   
cvck                                                    0.036024   
cvcv                                                    0.642121   
cvqd                                                    0.333333   
cvr                                                     7.322442   
cvm                                                          1.0   
cvmed                                                   0.998515   
cvmode         0    0.665677
Name: trip_duration_seconds, dty...   

column                                  trip_distance_kilometers  
rows                                                        4482  
sum                                                  7575.318998  
mean                                                    1.690165  
median                                                   1.31301  
mode           0     0.101606
1     0.104267
2     0.441151
3...  
max                                                    12.128969  
min                                                     0.100057  
std_dev                                                  1.38563  
variance                                                 1.91997  
skewness                                                1.985092  
kurtosis                                                6.083468  
percentile_25                                           0.744561  
percentile_75                                           2.209071  
iqr                                                      1.46451  
range                                                  12.028912  
cv                                                      0.819819  
qd                                                      0.495834  
cs                                                      1.432628  
ck                                                      4.390399  
cvs                                                     1.432628  
cvk                                                     4.390399  
cvcs                                                    1.432628  
cvck                                                    4.390399  
cvcv                                                    0.819819  
cvqd                                                    0.495834  
cvr                                                     7.117005  
cvm                                                          1.0  
cvmed                                                   0.776853  
cvmode         0

In [223]:
# get entries where trips start and end at station
evening_rush_delay_next_station_station = evening_rush_delay_next[evening_rush_delay_next['end_stop_id'].notna() & evening_rush_delay_next['start_stop_id'].notna()]
evening_rush_delay_next_station_station

nextbike_trips_id nextbike_trips_start_time nextbike_trips_end_time  \
1287486           37872114       2023-07-01 17:06:00     2023-07-01 17:16:00   
1668989           37800408       2023-07-01 17:06:00     2023-07-01 17:16:00   
1458370           37973456       2023-07-01 17:11:00     2023-07-01 17:16:00   
1334805           37894609       2023-07-01 17:11:00     2023-07-01 17:26:00   
1220395           37717934       2023-07-01 17:16:00     2023-07-01 17:26:00   
...                    ...                       ...                     ...   
1618858           38152683       2023-07-31 18:56:00     2023-07-31 19:01:00   
1436086           38007896       2023-07-31 19:01:00     2023-07-31 19:16:00   
1555579           38113933       2023-07-31 19:01:00     2023-07-31 19:21:00   
1638352           37769771       2023-07-31 19:31:00     2023-07-31 19:51:00   
1321268           37888438       2023-07-31 19:36:00     2023-07-31 19:46:00   

         nextbike_trips_start_at_station  nextbike_trips_end_at_station  \
1287486                            False                          False   
1668989                             True                          False   
1458370                             True                          False   
1334805                            False                          False   
1220395                            False                          False   
...                                  ...                            ...   
1618858                            False                          False   
1436086                            False                          False   
1555579                            False                           True   
1638352                            False                          False   
1321268                            False                          False   

        vehicle type   trip_duration  trip_distance_kilometers  \
1287486         bike 0 days 00:10:00                  0.148911   
1668989         bike 0 days 00:10:00                  1.313219   
1458370         bike 0 days 00:05:00                  0.431904   
1334805         bike 0 days 00:15:00                  2.293355   
1220395         bike 0 days 00:10:00                  2.084287   
...              ...             ...                       ...   
1618858         bike 0 days 00:05:00                  0.144827   
1436086         bike 0 days 00:15:00                  1.474985   
1555579         bike 0 days 00:20:00                  1.409239   
1638352         bike 0 days 00:20:00                  3.678575   
1321268         bike 0 days 00:10:00                  0.639235   

         trip_distance_meters  \
1287486            148.911114   
1668989           1313.218705   
1458370            431.903635   
1334805           2293.354991   
1220395           2084.287000   
...                       ...   
1618858            144.827122   
1436086           1474.984706   
1555579           1409.238698   
1638352           3678.575079   
1321268            639.235079   

                                            start_location  \
1287486  b'\x01\x01\x00\x00\x00\xea<*\xfe\xefh\x1c@uYLl...   
1668989  b'\x01\x01\x00\x00\x00\xa6}s\x7f\xf5h\x1c@\x92...   
1458370  b'\x01\x01\x00\x00\x00\x1c`\xe6;\xf8Y\x1c@.\xe...   
1334805  b'\x01\x01\x00\x00\x00\xb55"\x18\x07g\x1c@.\x1...   
1220395  b'\x01\x01\x00\x00\x00\x0c\xcc\nE\xba?\x1c@\xf...   
...                                                    ...   
1618858  b'\x01\x01\x00\x00\x00f\xf8O7P`\x1c@\x02eS\xae...   
1436086  b'\x01\x01\x00\x00\x00r\x8cd\x8fPc\x1c@2\x02*\...   
1555579  b'\x01\x01\x00\x00\x00\xd8b\xb7\xcf*c\x1c@1\xc...   
1638352  b'\x01\x01\x00\x00\x00\xb5\x8c\xd4{*w\x1c@\xcf...   
1321268  b'\x01\x01\x00\x00\x00\xdc\xbcqR\x98W\x1c@_\x0...   

                                              end_location  start_stop_id  \
1287486  b'\x01\x01\x00\x00\x00.py\xac\x19i\x1c@\x11p\x...         1115.0   
1668989  b'\x01\x01\x00\x00\x00j\x15\xfd\xa1\x99g\x1c@\...

In [224]:
evening_rush_delay_next_station_station.describe()

nextbike_trips_id      nextbike_trips_start_time  \
count       1.969000e+03                           1969   
mean        3.793836e+07  2023-07-15 18:12:42.691721472   
min         3.771661e+07            2023-07-01 17:06:00   
25%         3.782487e+07            2023-07-08 18:46:00   
50%         3.793951e+07            2023-07-14 17:46:00   
75%         3.804872e+07            2023-07-21 19:01:00   
max         3.817174e+07            2023-07-31 19:36:00   
std         1.293668e+05                            NaN   

             nextbike_trips_end_time              trip_duration  \
count                           1969                       1969   
mean   2023-07-15 18:26:30.015236352  0 days 00:13:47.323514474   
min              2023-07-01 17:16:00            0 days 00:05:00   
25%              2023-07-08 19:01:00            0 days 00:10:00   
50%              2023-07-14 18:01:00            0 days 00:10:00   
75%              2023-07-21 19:11:00            0 days 00:15:00   
max              2023-07-31 19:51:00            0 days 01:55:00   
std                              NaN  0 days 00:08:19.211774493   

       trip_distance_kilometers  trip_distance_meters  start_stop_id  \
count               1969.000000           1969.000000    1969.000000   
mean                   1.391081           1391.081118    1374.620620   
min                    0.100057            100.057033      43.000000   
25%                    0.681904            681.904024    1103.000000   
50%                    1.144335           1144.334567    1151.000000   
75%                    1.805832           1805.832364    1224.000000   
max                    8.239733           8239.732519    9780.000000   
std                    1.063761           1063.761260    1299.600366   

       end_stop_id  trip_duration_seconds  
count  1969.000000            1969.000000  
mean   1394.281361             827.323514  
min      43.000000             300.000000  
25%    1106.000000             600.000000  
50%    1153.000000             600.000000  
75%    1224.000000             900.000000  
max    9780.000000            6900.000000  
std    1375.566753             499.211774

In [225]:
# get statistics for the tier trips that start and end at a station
get_stats(evening_rush_delay_next_station_station, ['trip_duration_seconds', 'trip_distance_kilometers'])

column                                     trip_duration_seconds  \
rows                                                        1969   
sum                                                    1629000.0   
mean                                                  827.323514   
median                                                     600.0   
mode           0    600.0
Name: trip_duration_seconds, dtype:...   
max                                                       6900.0   
min                                                        300.0   
std_dev                                               499.211774   
variance                                           249212.395793   
skewness                                                3.458867   
kurtosis                                               22.987266   
percentile_25                                              600.0   
percentile_75                                              900.0   
iqr                                                        300.0   
range                                                     6600.0   
cv                                                      0.603406   
qd                                                           0.2   
cs                                                      0.006929   
ck                                                      0.046047   
cvs                                                     0.006929   
cvk                                                     0.046047   
cvcs                                                    0.006929   
cvck                                                    0.046047   
cvcv                                                    0.603406   
cvqd                                                         0.2   
cvr                                                     7.977532   
cvm                                                          1.0   
cvmed                                                    0.72523   
cvmode         0    0.72523
Name: trip_duration_seconds, dtyp...   

column                                  trip_distance_kilometers  
rows                                                        1969  
sum                                                  2739.038721  
mean                                                    1.391081  
median                                                  1.144335  
mode           0    0.101606
1    0.104267
2    0.441151
3   ...  
max                                                     8.239733  
min                                                     0.100057  
std_dev                                                 1.063761  
variance                                                1.131588  
skewness                                                1.975086  
kurtosis                                                6.058449  
percentile_25                                           0.681904  
percentile_75                                           1.805832  
iqr                                                     1.123928  
range                                                   8.139675  
cv                                                      0.764701  
qd                                                      0.451788  
cs                                                      1.856701  
ck                                                      5.695309  
cvs                                                     1.856701  
cvk                                                     5.695309  
cvcs                                                    1.856701  
cvck                                                    5.695309  
cvcv                                                    0.764701  
cvqd                                                    0.451788  
cvr                                                     5.851331  
cvm                                                          1.0  
cvmed                                                   0.822622  
cvmode         0

In [226]:
evening_rush_no_delay = no_delay[(no_delay['scheduled_arrival_time'].dt.hour >= 17) & (no_delay['scheduled_arrival_time'].dt.hour <= 19)]
evening_rush_no_delay

route_id  agency_id route_short_name  route_type route_type_name  \
54780         600          6              600           3             Bus   
54782          63          6               63           0            Tram   
54788         845         12              845           3             Bus   
54789         601          6              601           3             Bus   
54795         608          6              608           3             Bus   
...           ...        ...              ...         ...             ...   
2549884       630          6              630           3             Bus   
2549892       633          6              633           3             Bus   
2549894       609          6              609           3             Bus   
2549898       608          6              608           3             Bus   
2549899       884         12              884           3             Bus   

                                         agency_name  service_id  \
54780              SWB Stadtwerke Bonn Verkehrs GmbH         130   
54782              SWB Stadtwerke Bonn Verkehrs GmbH         130   
54788    RVK Regionalverkehr Köln GmbH NL Meckenheim         130   
54789              SWB Stadtwerke Bonn Verkehrs GmbH         130   
54795              SWB Stadtwerke Bonn Verkehrs GmbH         130   
...                                              ...         ...   
2549884            SWB Stadtwerke Bonn Verkehrs GmbH          64   
2549892            SWB Stadtwerke Bonn Verkehrs GmbH          64   
2549894            SWB Stadtwerke Bonn Verkehrs GmbH          64   
2549898            SWB Stadtwerke Bonn Verkehrs GmbH          64   
2549899  RVK Regionalverkehr Köln GmbH NL Meckenheim       27690   

                                                   trip_id  \
54780    6000370-600-006-8813.2.22:163900-32-1_A4B6A868...   
54782    630181-63-006-371.1.11:165500-18-1_99C2A22A-99...   
54788    1035-845-012-687.2.28:164800-29-1_D9CBC066-3E0...   
54789    6010219-601-006-1293.2.21:160100-46-1_0C4BA847...   
54795    6080185-608-006-1374.2.21:164200-46-1_C6F0646E...   
...                                                    ...   
2549884  6300058-630-006-9478.2.22:195500-50-1_52B6A95B...   
2549892  6330062-633-006-1584.2.24:194300-24-1_D28C05E2...   
2549894  6090126-609-006-1574.2.24:191900-45-1_6C4426EF...   
2549898  6080117-608-006-1374.2.21:192100-46-1_F091AAE0...   
2549899  58-884-012-3332.2.22:195100-16-1_8E173F5D-3446...   

                trip_headsign  direction_id  ...  delay_span  \
54780     Ippendorf Altenheim             1  ...           0   
54782       Tannenbusch Mitte             0  ...           0   
54788                 Fronhof             0  ...           0   
54789      Agnetendorfer Str.             0  ...           0   
54795                 Gielgen             0  ...           0   
...                       ...           ...  ...         ...   
2549884       Uniklinikum Süd             1  ...           0   
2549892      Endenich Nord Bf             1  ...         0-5   
2549894    Hardthöhe/Südwache             1  ...           0   
2549898               Gielgen             0  ...         0-5   
2549899  Lessenich Sportplatz             1  ...           0   

         arrival_delay_span weather_int time_span_arrival  \
54780                     0           0         afternoon   
54782                     0           0         afternoon   
54788                     0           0                 0   
54789                     0           0         afternoon   
54795                     0           0         afternoon   
...                     ...         ...               ...   
2549884                   0           1      evening rush   
2549892                   0           1                 0   
2549894                   0           1      evening rush   
2549898                   0           1                 0   
2549899                   0           1                 0   

         time_span_i

In [227]:
get_stats(evening_rush_no_delay, ['tier_trips_count', 'tier_trips_end_at_station_count', 'nextbike_trips_count', 'nextbike_trips_end_at_station_count', 'current_temp', 'current_precipitation_volume'])

/tmp/ipykernel_2575952/41814695.py:51: RuntimeWarning: invalid value encountered in scalar divide
  qd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:55: RuntimeWarning: invalid value encountered in scalar divide
  cvqd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:51: RuntimeWarning: invalid value encountered in scalar divide
  qd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:55: RuntimeWarning: invalid value encountered in scalar divide
  cvqd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:51: RuntimeWarning: invalid value encountered in scalar divide
  qd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:55: RuntimeWarning: invalid value encountered in scalar divide
  cvqd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:51: RuntimeWarning: invalid value encountered in scalar divide
  qd = iqr / (percentile_75 + percenti

column                                        tier_trips_count  \
rows                                                    105539   
sum                                                       3952   
mean                                                  0.037446   
median                                                     0.0   
mode               0    0
Name: tier_trips_count, dtype: int64   
max                                                          6   
min                                                          0   
std_dev                                               0.224687   
variance                                              0.050484   
skewness                                              7.518018   
kurtosis                                              74.64147   
percentile_25                                              0.0   
percentile_75                                              0.0   
iqr                                                        0.0   
range                                                        6   
cv                                                    6.000318   
qd                                                         NaN   
cs                                                   33.459939   
ck                                                  332.201768   
cvs                                                  33.459939   
cvk                                                 332.201768   
cvcs                                                 33.459939   
cvck                                                332.201768   
cvcv                                                  6.000318   
cvqd                                                       NaN   
cvr                                                 160.231275   
cvm                                                        1.0   
cvmed                                                      0.0   
cvmode         0    0.0
Name: tier_trips_count, dtype: float64   

column                           tier_trips_end_at_station_count  \
rows                                                      105539   
sum                                                         3138   
mean                                                    0.029733   
median                                                       0.0   
mode           0    0
Name: tier_trips_end_at_station_count, ...   
max                                                            4   
min                                                            0   
std_dev                                                 0.197741   
variance                                                0.039102   
skewness                                                8.244007   
kurtosis                                               87.225278   
percentile_25                                                0.0   
percentile_75                                                0.0   
iqr                                                          0.0   
range                                                          4   
cv                                                       6.65054   
qd                                                           NaN   
cs                                                     41.690918   
ck                                                    441.108545   
cvs                                                    41.690918   
cvk                                                   441.108545   
cvcs                                                   41.690918   
cvck                                                  441.108545   
cvcv                                                     6.65054   
cvqd                                                         NaN   
cvr                                                   134.530274   
cvm                                                          1.0   
cvmed                                                        0.0   
cvmode         0    0.0
Name: tier_trips_end_at

In [228]:
evening_rush_no_delay_tier = check_micromobility_datasets('tier', evening_rush_no_delay)

In [229]:
evening_rush_no_delay_tier.describe()

tier_trips_id          tier_trips_start_time  \
count   1.465000e+03                           1465   
mean    7.997511e+08  2023-07-15 23:54:21.501706496   
min     7.822649e+08            2023-07-01 17:00:00   
25%     7.823837e+08            2023-07-08 18:05:00   
50%     8.086430e+08            2023-07-14 18:35:00   
75%     8.087580e+08            2023-07-22 19:00:00   
max     8.323115e+08            2023-07-31 19:30:00   
std     1.687527e+07                            NaN   

                 tier_trips_end_time              trip_duration  \
count                           1465                       1465   
mean   2023-07-16 00:08:42.389078784  0 days 00:14:20.887372013   
min              2023-07-01 17:15:00            0 days 00:05:00   
25%              2023-07-08 18:15:00            0 days 00:10:00   
50%              2023-07-14 18:50:00            0 days 00:10:00   
75%              2023-07-22 19:15:00            0 days 00:15:00   
max              2023-07-31 19:55:00            0 days 02:00:00   
std                              NaN  0 days 00:10:31.552453601   

       trip_distance_kilometers  trip_distance_meters  start_stop_id  \
count               1465.000000           1465.000000    1113.000000   
mean                   1.683478           1683.478196    1202.500449   
min                    0.101712            101.712154     161.000000   
25%                    0.706364            706.364143     687.000000   
50%                    1.320052           1320.052067    1115.000000   
75%                    2.218750           2218.749637    1406.000000   
max                   11.565806          11565.805864    9703.000000   
std                    1.392559           1392.559369    1108.969341   

       end_stop_id  trip_duration_seconds  
count   687.000000            1465.000000  
mean   1531.790393             860.887372  
min      43.000000             300.000000  
25%    1110.000000             600.000000  
50%    1151.000000             600.000000  
75%    1284.500000             900.000000  
max    9703.000000            7200.000000  
std    1624.834145             631.552454

In [230]:
get_stats(evening_rush_no_delay_tier, ['trip_duration_seconds', 'trip_distance_kilometers'])

column                                     trip_duration_seconds  \
rows                                                        1465   
sum                                                    1261200.0   
mean                                                  860.887372   
median                                                     600.0   
mode           0    600.0
Name: trip_duration_seconds, dtype:...   
max                                                       7200.0   
min                                                        300.0   
std_dev                                               631.552454   
variance                                           398858.501651   
skewness                                                4.061743   
kurtosis                                               25.979322   
percentile_25                                              600.0   
percentile_75                                              900.0   
iqr                                                        300.0   
range                                                     6900.0   
cv                                                      0.733606   
qd                                                           0.2   
cs                                                      0.006431   
ck                                                      0.041136   
cvs                                                     0.006431   
cvk                                                     0.041136   
cvcs                                                    0.006431   
cvck                                                    0.041136   
cvcv                                                    0.733606   
cvqd                                                         0.2   
cvr                                                     8.014986   
cvm                                                          1.0   
cvmed                                                   0.696955   
cvmode         0    0.696955
Name: trip_duration_seconds, dty...   

column                                  trip_distance_kilometers  
rows                                                        1465  
sum                                                  2466.295557  
mean                                                    1.683478  
median                                                  1.320052  
mode           0        0.101712
1        0.101896
2        0...  
max                                                    11.565806  
min                                                     0.101712  
std_dev                                                 1.392559  
variance                                                1.939222  
skewness                                                1.935025  
kurtosis                                                5.651086  
percentile_25                                           0.706364  
percentile_75                                            2.21875  
iqr                                                     1.512385  
range                                                  11.464094  
cv                                                      0.827192  
qd                                                      0.517035  
cs                                                      1.389546  
ck                                                      4.058057  
cvs                                                     1.389546  
cvk                                                     4.058057  
cvcs                                                    1.389546  
cvck                                                    4.058057  
cvcv                                                    0.827192  
cvqd                                                    0.517035  
cvr                                                     6.809767  
cvm                                                          1.0  
cvmed                                                   0.784122  
cvmode         0

In [231]:
# get entries where trips start and end at station
evening_rush_no_delay_tier_station_station = evening_rush_no_delay_tier[evening_rush_no_delay_tier['end_stop_id'].notna() & evening_rush_no_delay_tier['start_stop_id'].notna()]
evening_rush_no_delay_tier_station_station

tier_trips_id tier_trips_start_time tier_trips_end_time vehicle type  \
3035496      782304577   2023-07-01 17:10:00 2023-07-01 17:20:00    e-scooter   
2954000      782279912   2023-07-01 17:15:00 2023-07-01 17:25:00    e-scooter   
3125894      782334920   2023-07-01 17:15:00 2023-07-01 17:25:00    e-scooter   
3200651      782382402   2023-07-01 17:20:00 2023-07-01 17:30:00    e-scooter   
2954001      782279913   2023-07-01 17:30:00 2023-07-01 17:45:00    e-scooter   
...                ...                   ...                 ...          ...   
3474518      832255157   2023-07-31 18:55:00 2023-07-31 19:15:00    e-scooter   
3329638      832127671   2023-07-31 19:00:00 2023-07-31 19:05:00    e-scooter   
3406919      832190324   2023-07-31 19:10:00 2023-07-31 19:15:00    e-scooter   
3485590      832265811   2023-07-31 19:25:00 2023-07-31 19:30:00    e-scooter   
3325496      832124855   2023-07-31 19:25:00 2023-07-31 19:40:00    e-scooter   

          trip_duration  trip_distance_kilometers  trip_distance_meters  \
3035496 0 days 00:10:00                  1.576509           1576.508878   
2954000 0 days 00:10:00                  1.327481           1327.480919   
3125894 0 days 00:10:00                  0.118998            118.997600   
3200651 0 days 00:10:00                  0.343392            343.391843   
2954001 0 days 00:15:00                  2.267151           2267.150628   
...                 ...                       ...                   ...   
3474518 0 days 00:20:00                  0.276712            276.712428   
3329638 0 days 00:05:00                  0.131171            131.170869   
3406919 0 days 00:05:00                  0.369476            369.475607   
3485590 0 days 00:05:00                  0.212159            212.159418   
3325496 0 days 00:15:00                  2.200121           2200.120734   

         start_stop_id                            start_stop_name  \
3035496         1102.0                         Bonn Friedensplatz   
2954000         1104.0                             Bonn Stadthaus   
3125894          694.0                     Bonn Tannenbusch Mitte   
3200651          687.0                                   Bonn Hbf   
2954001          688.0                                  Bonn West   
...                ...                                        ...   
3474518         1115.0  Bonn Bertha-Von-Suttner-Pl./Beethovenhaus   
3329638         2667.0  Bonn Brüdergasse/Bertha-Von-Suttner-Platz   
3406919         1102.0                         Bonn Friedensplatz   
3485590         1103.0                                 Bonn Markt   
3325496         1522.0                                Bonn Vilich   

                                         start_buffer_zone  end_stop_id  \
3035496  801621     POLYGON ((7.157885983913106 50.7227...       1192.0   
2954000  801621     POLYGON ((7.157885983913106 50.7227...        688.0   
3125894  801621     POLYGON ((7.157885983913106 50.7227...        694.0   
3200651  801621     POLYGON ((7.157885983913106 50.7227...       1144.0   
2954001  801621     POLYGON ((7.157885983913106 50.7227...       8506.0   
...                                                    ...          ...   
3474518  801621     POLYGON ((7.157885983913106 50.7227...       1115.0   
3329638  801621     POLYGON ((7.157885983913106 50.7227...       2667.0   
3406919  801621     POLYGON ((7.157885983913106 50.7227...        687.0   
3485590  801621     POLYGON ((7.157885983913106 50.7227...        686.0   
3325496  801621     POLYGON ((7.157885983913106 50.7227...       1521.0   

                                     end_stop_name  \
3035496                             Bonn Ellerstr.   
2954000                                  Bonn West   
3125894                     Bonn Tannenbusch Mitte   
3200651                         Bonn Beethovenstr.   
2954001                             Bonn Werftstr.   
...                                            ...   
3474518  Bonn Bertha-Von-Su

In [232]:
evening_rush_no_delay_tier_station_station.describe()

tier_trips_id          tier_trips_start_time  \
count   6.140000e+02                            614   
mean    7.998238e+08  2023-07-15 18:41:51.889251072   
min     7.822649e+08            2023-07-01 17:10:00   
25%     7.823791e+08            2023-07-07 19:41:15   
50%     8.086373e+08            2023-07-14 17:20:00   
75%     8.087596e+08            2023-07-22 19:05:00   
max     8.323009e+08            2023-07-31 19:25:00   
std     1.728552e+07                            NaN   

                 tier_trips_end_time              trip_duration  \
count                            614                        614   
mean   2023-07-15 18:55:10.260586496  0 days 00:13:18.371335504   
min              2023-07-01 17:20:00            0 days 00:05:00   
25%              2023-07-07 20:20:00            0 days 00:10:00   
50%              2023-07-14 17:32:30            0 days 00:10:00   
75%              2023-07-22 19:16:15            0 days 00:15:00   
max              2023-07-31 19:40:00            0 days 01:40:00   
std                              NaN  0 days 00:10:13.255388754   

       trip_distance_kilometers  trip_distance_meters  start_stop_id  \
count                614.000000            614.000000     614.000000   
mean                   1.428391           1428.390916    1253.778502   
min                    0.101712            101.712154     161.000000   
25%                    0.623435            623.435359     687.000000   
50%                    1.142161           1142.161419    1115.000000   
75%                    1.950278           1950.277619    1221.000000   
max                    8.442163           8442.163487    9702.000000   
std                    1.143488           1143.487916    1176.228120   

       end_stop_id  trip_duration_seconds  
count   614.000000             614.000000  
mean   1576.052117             798.371336  
min      43.000000             300.000000  
25%    1110.000000             600.000000  
50%    1151.000000             600.000000  
75%    1252.250000             900.000000  
max    9703.000000            6000.000000  
std    1703.666569             613.255389

In [233]:
# get statistics for the tier trips that start and end at a station
get_stats(evening_rush_no_delay_tier_station_station, ['trip_duration_seconds', 'trip_distance_kilometers'])

column                                     trip_duration_seconds  \
rows                                                         614   
sum                                                     490200.0   
mean                                                  798.371336   
median                                                     600.0   
mode           0    600.0
Name: trip_duration_seconds, dtype:...   
max                                                       6000.0   
min                                                        300.0   
std_dev                                               613.255389   
variance                                           376082.171836   
skewness                                                4.728527   
kurtosis                                               31.821014   
percentile_25                                              600.0   
percentile_75                                              900.0   
iqr                                                        300.0   
range                                                     5700.0   
cv                                                      0.768133   
qd                                                           0.2   
cs                                                      0.007711   
ck                                                      0.051889   
cvs                                                     0.007711   
cvk                                                     0.051889   
cvcs                                                    0.007711   
cvck                                                    0.051889   
cvcv                                                    0.768133   
cvqd                                                         0.2   
cvr                                                     7.139535   
cvm                                                          1.0   
cvmed                                                    0.75153   
cvmode         0    0.75153
Name: trip_duration_seconds, dtyp...   

column                                  trip_distance_kilometers  
rows                                                         614  
sum                                                   877.032023  
mean                                                    1.428391  
median                                                  1.142161  
mode           0      0.101712
1      0.105218
2      0.11105...  
max                                                     8.442163  
min                                                     0.101712  
std_dev                                                 1.143488  
variance                                                1.307565  
skewness                                                1.787656  
kurtosis                                                 4.83512  
percentile_25                                           0.623435  
percentile_75                                           1.950278  
iqr                                                     1.326842  
range                                                   8.340451  
cv                                                      0.800543  
qd                                                      0.515536  
cs                                                      1.563336  
ck                                                      4.228397  
cvs                                                     1.563336  
cvk                                                     4.228397  
cvcs                                                    1.563336  
cvck                                                    4.228397  
cvcv                                                    0.800543  
cvqd                                                    0.515536  
cvr                                                     5.839054  
cvm                                                          1.0  
cvmed                                                   0.799614  
cvmode         0

In [234]:
evening_rush_no_delay_next = check_micromobility_datasets('next', evening_rush_no_delay)

In [235]:
evening_rush_no_delay_next.describe()

nextbike_trips_id      nextbike_trips_start_time  \
count       3.354000e+03                           3354   
mean        3.793718e+07  2023-07-16 09:00:14.472271872   
min         3.771656e+07            2023-07-01 17:01:00   
25%         3.782136e+07            2023-07-08 19:46:00   
50%         3.793563e+07            2023-07-15 18:16:00   
75%         3.805118e+07            2023-07-22 19:11:00   
max         3.817169e+07            2023-07-31 20:01:00   
std         1.308097e+05                            NaN   

             nextbike_trips_end_time              trip_duration  \
count                           3354                       3354   
mean   2023-07-16 09:15:07.227191552  0 days 00:14:52.754919499   
min              2023-07-01 17:11:00            0 days 00:05:00   
25%              2023-07-08 20:01:00            0 days 00:10:00   
50%              2023-07-15 18:28:30            0 days 00:10:00   
75%              2023-07-22 19:26:00            0 days 00:15:00   
max              2023-07-31 20:16:00            0 days 01:55:00   
std                              NaN  0 days 00:09:40.098910841   

       trip_distance_kilometers  trip_distance_meters  start_stop_id  \
count               3354.000000           3354.000000    2715.000000   
mean                   1.673183           1673.183110    1179.499448   
min                    0.100260            100.260461     161.000000   
25%                    0.772043            772.043132     687.000000   
50%                    1.300183           1300.182511    1115.000000   
75%                    2.113716           2113.716286    1221.000000   
max                   13.237596          13237.595651    9780.000000   
std                    1.403555           1403.554563    1057.671381   

       end_stop_id  trip_duration_seconds  
count  1817.000000            3354.000000  
mean   1328.625757             892.754919  
min      43.000000             300.000000  
25%    1104.000000             600.000000  
50%    1153.000000             600.000000  
75%    1224.000000             900.000000  
max    9780.000000            6900.000000  
std    1220.029470             580.098911

In [236]:
get_stats(evening_rush_no_delay_next, ['trip_duration_seconds', 'trip_distance_kilometers'])

column                                     trip_duration_seconds  \
rows                                                        3354   
sum                                                    2994300.0   
mean                                                  892.754919   
median                                                     600.0   
mode           0    600.0
Name: trip_duration_seconds, dtype:...   
max                                                       6900.0   
min                                                        300.0   
std_dev                                               580.098911   
variance                                            336514.74636   
skewness                                                 3.48512   
kurtosis                                               20.563471   
percentile_25                                              600.0   
percentile_75                                              900.0   
iqr                                                        300.0   
range                                                     6600.0   
cv                                                      0.649785   
qd                                                           0.2   
cs                                                      0.006008   
ck                                                      0.035448   
cvs                                                     0.006008   
cvk                                                     0.035448   
cvcs                                                    0.006008   
cvck                                                    0.035448   
cvcv                                                    0.649785   
cvqd                                                         0.2   
cvr                                                     7.392846   
cvm                                                          1.0   
cvmed                                                   0.672077   
cvmode         0    0.672077
Name: trip_duration_seconds, dty...   

column                                  trip_distance_kilometers  
rows                                                        3354  
sum                                                   5611.85615  
mean                                                    1.673183  
median                                                  1.300183  
mode           0    0.101606
1    0.383186
2    0.831845
3   ...  
max                                                    13.237596  
min                                                      0.10026  
std_dev                                                 1.403555  
variance                                                1.969965  
skewness                                                2.290226  
kurtosis                                                8.523387  
percentile_25                                           0.772043  
percentile_75                                           2.113716  
iqr                                                     1.341673  
range                                                  13.137335  
cv                                                      0.838853  
qd                                                      0.464929  
cs                                                      1.631733  
ck                                                      6.072715  
cvs                                                     1.631733  
cvk                                                     6.072715  
cvcs                                                    1.631733  
cvck                                                    6.072715  
cvcv                                                    0.838853  
cvqd                                                    0.464929  
cvr                                                     7.851702  
cvm                                                          1.0  
cvmed                                                   0.777071  
cvmode         0

In [237]:
# get entries where trips start and end at station
evening_rush_no_delay_next_station_station = evening_rush_no_delay_next[evening_rush_no_delay_next['end_stop_id'].notna() & evening_rush_no_delay_next['start_stop_id'].notna()]
evening_rush_no_delay_next_station_station

nextbike_trips_id nextbike_trips_start_time nextbike_trips_end_time  \
1505010           38062285       2023-07-01 17:01:00     2023-07-01 17:16:00   
1555237           38113591       2023-07-01 17:06:00     2023-07-01 17:26:00   
1334805           37894609       2023-07-01 17:11:00     2023-07-01 17:26:00   
1293982           37875072       2023-07-01 17:26:00     2023-07-01 17:36:00   
1534484           38085499       2023-07-01 17:26:00     2023-07-01 17:36:00   
...                    ...                       ...                     ...   
1290123           37839777       2023-07-31 19:21:00     2023-07-31 19:31:00   
1539402           38089360       2023-07-31 19:31:00     2023-07-31 19:41:00   
1638352           37769771       2023-07-31 19:31:00     2023-07-31 19:51:00   
1377018           37916580       2023-07-31 19:41:00     2023-07-31 19:51:00   
1237673           37728341       2023-07-31 20:01:00     2023-07-31 20:16:00   

         nextbike_trips_start_at_station  nextbike_trips_end_at_station  \
1505010                            False                          False   
1555237                            False                          False   
1334805                            False                          False   
1293982                             True                          False   
1534484                            False                          False   
...                                  ...                            ...   
1290123                            False                          False   
1539402                            False                           True   
1638352                            False                          False   
1377018                            False                          False   
1237673                             True                          False   

        vehicle type   trip_duration  trip_distance_kilometers  \
1505010         bike 0 days 00:15:00                  0.963955   
1555237         bike 0 days 00:20:00                  1.766626   
1334805         bike 0 days 00:15:00                  2.293355   
1293982         bike 0 days 00:10:00                  1.155661   
1534484         bike 0 days 00:10:00                  1.048712   
...              ...             ...                       ...   
1290123         bike 0 days 00:10:00                  1.040513   
1539402         bike 0 days 00:10:00                  0.814886   
1638352         bike 0 days 00:20:00                  3.678575   
1377018         bike 0 days 00:10:00                  0.736360   
1237673         bike 0 days 00:15:00                  1.896784   

         trip_distance_meters  \
1505010            963.954661   
1555237           1766.626256   
1334805           2293.354991   
1293982           1155.660576   
1534484           1048.712047   
...                       ...   
1290123           1040.512967   
1539402            814.886181   
1638352           3678.575079   
1377018            736.359754   
1237673           1896.783943   

                                            start_location  \
1505010  b'\x01\x01\x00\x00\x00\xbd\xab\x1e0\x0fY\x1c@\...   
1555237  b'\x01\x01\x00\x00\x00u\xc7b\x9bTd\x1c@=\xd5!7...   
1334805  b'\x01\x01\x00\x00\x00\xb55"\x18\x07g\x1c@.\x1...   
1293982  b'\x01\x01\x00\x00\x00\xbf\xf4\xf6\xe7\xa2\x81...   
1534484  b'\x01\x01\x00\x00\x00\x17\xd6\x8dwGf\x1c@\xa2...   
...                                                    ...   
1290123  b'\x01\x01\x00\x00\x00{/\xbeh\x8fg\x1c@\xac\x8...   
1539402  b'\x01\x01\x00\x00\x00/\xc3\x7f\xba\x81b\x1c@h...   
1638352  b'\x01\x01\x00\x00\x00\xb5\x8c\xd4{*w\x1c@\xcf...   
1377018  b'\x01\x01\x00\x00\x00\xcd\xc8 w\x11v\x1c@l\xb...   
1237673  b'\x01\x01\x00\x00\x00\xbf\xf4\xf6\xe7\xa2\x81...   

                                              end_location  start_stop_id  \
1505010  b'\x01\x01\x00\x00\x00E\xba\x9fS\x90_\x1c@4\x9...         1140.0   
1555237  b'\x01\x01\x00\x00\x00v\xfb\xac2Sj\x1c@T7\x17\...

In [238]:
evening_rush_no_delay_next_station_station.describe()

nextbike_trips_id      nextbike_trips_start_time  \
count       1.595000e+03                           1595   
mean        3.793992e+07  2023-07-16 10:11:47.021943808   
min         3.771680e+07            2023-07-01 17:01:00   
25%         3.782232e+07            2023-07-09 17:01:00   
50%         3.793990e+07            2023-07-15 18:46:00   
75%         3.805630e+07            2023-07-22 18:56:00   
max         3.817169e+07            2023-07-31 20:01:00   
std         1.313580e+05                            NaN   

             nextbike_trips_end_time              trip_duration  \
count                           1595                       1595   
mean   2023-07-16 10:25:25.015674112  0 days 00:13:37.993730407   
min              2023-07-01 17:16:00            0 days 00:05:00   
25%              2023-07-09 17:11:00            0 days 00:10:00   
50%              2023-07-15 19:01:00            0 days 00:10:00   
75%              2023-07-22 19:18:30            0 days 00:15:00   
max              2023-07-31 20:16:00            0 days 01:55:00   
std                              NaN  0 days 00:08:37.482068581   

       trip_distance_kilometers  trip_distance_meters  start_stop_id  \
count               1595.000000           1595.000000    1595.000000   
mean                   1.379578           1379.578038    1238.477116   
min                    0.100260            100.260461     161.000000   
25%                    0.704471            704.471010     687.000000   
50%                    1.121271           1121.271226    1115.000000   
75%                    1.760046           1760.045916    1184.000000   
max                    7.902944           7902.943643    9780.000000   
std                    1.080013           1080.013144    1167.008495   

       end_stop_id  trip_duration_seconds  
count  1595.000000            1595.000000  
mean   1347.035110             817.993730  
min      43.000000             300.000000  
25%    1110.000000             600.000000  
50%    1153.000000             600.000000  
75%    1224.000000             900.000000  
max    9780.000000            6900.000000  
std    1224.323383             517.482069

In [239]:
# get statistics for the tier trips that start and end at a station
get_stats(evening_rush_no_delay_next_station_station, ['trip_duration_seconds', 'trip_distance_kilometers'])

column                                     trip_duration_seconds  \
rows                                                        1595   
sum                                                    1304700.0   
mean                                                   817.99373   
median                                                     600.0   
mode           0    600.0
Name: trip_duration_seconds, dtype:...   
max                                                       6900.0   
min                                                        300.0   
std_dev                                               517.482069   
variance                                           267787.691303   
skewness                                                3.924207   
kurtosis                                               27.911671   
percentile_25                                              600.0   
percentile_75                                              900.0   
iqr                                                        300.0   
range                                                     6600.0   
cv                                                      0.632624   
qd                                                           0.2   
cs                                                      0.007583   
ck                                                      0.053937   
cvs                                                     0.007583   
cvk                                                     0.053937   
cvcs                                                    0.007583   
cvck                                                    0.053937   
cvcv                                                    0.632624   
cvqd                                                         0.2   
cvr                                                     8.068521   
cvm                                                          1.0   
cvmed                                                   0.733502   
cvmode         0    0.733502
Name: trip_duration_seconds, dty...   

column                                  trip_distance_kilometers  
rows                                                        1595  
sum                                                   2200.42697  
mean                                                    1.379578  
median                                                  1.121271  
mode           0    0.101606
1    0.383186
2    1.398723
Name...  
max                                                     7.902944  
min                                                      0.10026  
std_dev                                                 1.080013  
variance                                                1.166428  
skewness                                                2.068302  
kurtosis                                                6.165025  
percentile_25                                           0.704471  
percentile_75                                           1.760046  
iqr                                                     1.055575  
range                                                   7.802683  
cv                                                      0.782858  
qd                                                      0.428309  
cs                                                      1.915071  
ck                                                      5.708287  
cvs                                                     1.915071  
cvk                                                     5.708287  
cvcs                                                    1.915071  
cvck                                                    5.708287  
cvcv                                                    0.782858  
cvqd                                                    0.428309  
cvr                                                     5.655848  
cvm                                                          1.0  
cvmed                                                   0.812764  
cvmode         0

In [240]:
evening_rush_nan_delay = nan_delay[(nan_delay['scheduled_arrival_time'].dt.hour >= 17) & (nan_delay['scheduled_arrival_time'].dt.hour <= 19)]
evening_rush_nan_delay

route_id  agency_id route_short_name  route_type route_type_name  \
54777         633          6              633           3             Bus   
54778         845         12              845           3             Bus   
54779          65          6               65           0            Tram   
54781          65          6               65           0            Tram   
54783         606          6              606           3             Bus   
...           ...        ...              ...         ...             ...   
2549883        65          6               65           0            Tram   
2549890       611          6              611           3             Bus   
2549891       609          6              609           3             Bus   
2549895       607          6              607           3             Bus   
2549896       604          6              604           3             Bus   

                                         agency_name  service_id  \
54777              SWB Stadtwerke Bonn Verkehrs GmbH         130   
54778    RVK Regionalverkehr Köln GmbH NL Meckenheim         130   
54779              SWB Stadtwerke Bonn Verkehrs GmbH       26814   
54781              SWB Stadtwerke Bonn Verkehrs GmbH       26814   
54783              SWB Stadtwerke Bonn Verkehrs GmbH         130   
...                                              ...         ...   
2549883            SWB Stadtwerke Bonn Verkehrs GmbH       26825   
2549890            SWB Stadtwerke Bonn Verkehrs GmbH          64   
2549891            SWB Stadtwerke Bonn Verkehrs GmbH          64   
2549895            SWB Stadtwerke Bonn Verkehrs GmbH       27234   
2549896            SWB Stadtwerke Bonn Verkehrs GmbH          64   

                                                   trip_id  \
54777    6330106-633-006-1584.2.24:164900-24-1_5B316B9C...   
54778    1638-845-012-1842.2.22:162000-29-1_13DCA082-AF...   
54779    650737-65-006-1593.1.12:165400-24-178_2F502D54...   
54781    650746-65-006-1406.1.12:165400-24-178_C0B4F493...   
54783    6060194-606-006-1584.2.22:165400-44-1_F94715C5...   
...                                                    ...   
2549883  651152-65-006-1406.1.12:194400-24-179_F4DE0E09...   
2549890  6110081-611-006-1723.2.21:185000-60-1_F891DCE8...   
2549891  6090124-609-006-1574.2.24:185900-45-1_A3A33C8A...   
2549895  6070130-607-006-1584.2.22:190300-46-1_55299A70...   
2549896  6040104-604-006-678.2.21:192300-51-1_77E706CC-...   

                       trip_headsign  direction_id  ...  delay_span  \
54777               Endenich Nord Bf             1  ...           0   
54778                       Bonn Hbf             1  ...           0   
54779              Kopenhagener Str.             0  ...           0   
54781    Oberkassel Süd/Römlinghoven             1  ...           0   
54783             Hardtberg Klinikum             1  ...           0   
...                              ...           ...  ...         ...   
2549883  Oberkassel Süd/Römlinghoven             1  ...           0   
2549890         Lessenich Sportplatz             0  ...           0   
2549891           Hardthöhe/Südwache             1  ...           0   
2549895           Hardtberg Klinikum             1  ...           0   
2549896              Ückesdorf Mitte             1  ...           0   

         arrival_delay_span weather_int time_span_arrival  \
54777                     0           0                 0   
54778                     0           0                 0   
54779                     0           0                 0   
54781                     0           0                 0   
54783                     0           0                 0   
...                     ...         ...               ...   
2549883                   0           1                 0   
2549890                   0           1                 0   
2549891                   0           1                 0   
2549895                   0           1                 0  

In [241]:
get_stats(evening_rush_nan_delay, ['tier_trips_count', 'tier_trips_end_at_station_count', 'nextbike_trips_count', 'nextbike_trips_end_at_station_count', 'current_temp', 'current_precipitation_volume'])

/tmp/ipykernel_2575952/41814695.py:51: RuntimeWarning: invalid value encountered in scalar divide
  qd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:55: RuntimeWarning: invalid value encountered in scalar divide
  cvqd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:51: RuntimeWarning: invalid value encountered in scalar divide
  qd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:55: RuntimeWarning: invalid value encountered in scalar divide
  cvqd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:51: RuntimeWarning: invalid value encountered in scalar divide
  qd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:55: RuntimeWarning: invalid value encountered in scalar divide
  cvqd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:51: RuntimeWarning: invalid value encountered in scalar divide
  qd = iqr / (percentile_75 + percenti

column                                        tier_trips_count  \
rows                                                    171041   
sum                                                       3917   
mean                                                  0.022901   
median                                                     0.0   
mode               0    0
Name: tier_trips_count, dtype: int64   
max                                                          6   
min                                                          0   
std_dev                                               0.170554   
variance                                              0.029088   
skewness                                              9.224182   
kurtosis                                            114.747585   
percentile_25                                              0.0   
percentile_75                                              0.0   
iqr                                                        0.0   
range                                                        6   
cv                                                    7.447445   
qd                                                         NaN   
cs                                                   54.083803   
ck                                                   672.79521   
cvs                                                  54.083803   
cvk                                                  672.79521   
cvcs                                                 54.083803   
cvck                                                 672.79521   
cvcv                                                  7.447445   
cvqd                                                       NaN   
cvr                                                 261.997958   
cvm                                                        1.0   
cvmed                                                      0.0   
cvmode         0    0.0
Name: tier_trips_count, dtype: float64   

column                           tier_trips_end_at_station_count  \
rows                                                      171041   
sum                                                         3057   
mean                                                    0.017873   
median                                                       0.0   
mode           0    0
Name: tier_trips_end_at_station_count, ...   
max                                                            4   
min                                                            0   
std_dev                                                 0.149335   
variance                                                0.022301   
skewness                                               10.199054   
kurtosis                                              134.716725   
percentile_25                                                0.0   
percentile_75                                                0.0   
iqr                                                          0.0   
range                                                          4   
cv                                                      8.355394   
qd                                                           NaN   
cs                                                     68.296391   
ck                                                    902.109748   
cvs                                                    68.296391   
cvk                                                   902.109748   
cvcs                                                   68.296391   
cvck                                                  902.109748   
cvcv                                                    8.355394   
cvqd                                                         NaN   
cvr                                                   223.802421   
cvm                                                          1.0   
cvmed                                                        0.0   
cvmode         0    0.0
Name: tier_trips_end_at

In [242]:
evening_rush_nan_delay_tier = check_micromobility_datasets('tier', evening_rush_nan_delay)

In [243]:
evening_rush_nan_delay_tier.describe()

tier_trips_id          tier_trips_start_time  \
count   2.035000e+03                           2035   
mean    7.999887e+08  2023-07-15 16:49:27.272727296   
min     7.822646e+08            2023-07-01 17:05:00   
25%     7.823835e+08            2023-07-07 17:50:00   
50%     8.086438e+08            2023-07-14 18:00:00   
75%     8.087578e+08            2023-07-23 17:15:00   
max     8.323115e+08            2023-07-31 19:45:00   
std     1.724155e+07                            NaN   

                 tier_trips_end_time              trip_duration  \
count                           2035                       2035   
mean   2023-07-15 17:04:05.012285184  0 days 00:14:37.739557739   
min              2023-07-01 17:15:00            0 days 00:05:00   
25%              2023-07-07 18:00:00            0 days 00:10:00   
50%              2023-07-14 18:10:00            0 days 00:10:00   
75%              2023-07-23 17:30:00            0 days 00:15:00   
max              2023-07-31 20:00:00            0 days 01:55:00   
std                              NaN  0 days 00:11:02.249972101   

       trip_distance_kilometers  trip_distance_meters  start_stop_id  \
count               2035.000000           2035.000000    1482.000000   
mean                   1.701737           1701.737070    1306.124831   
min                    0.100246            100.246164      43.000000   
25%                    0.697804            697.804297     687.000000   
50%                    1.299361           1299.360611    1115.000000   
75%                    2.227271           2227.271031    1311.000000   
max                   13.561161          13561.161418    9703.000000   
std                    1.493913           1493.912849    1303.929616   

       end_stop_id  trip_duration_seconds  
count   974.000000            2035.000000  
mean   1407.066735             877.739558  
min      43.000000             300.000000  
25%    1104.000000             600.000000  
50%    1151.000000             600.000000  
75%    1255.000000             900.000000  
max    9703.000000            6900.000000  
std    1392.995051             662.249972

In [244]:
get_stats(evening_rush_nan_delay_tier, ['trip_duration_seconds', 'trip_distance_kilometers'])

column                                     trip_duration_seconds  \
rows                                                        2035   
sum                                                    1786200.0   
mean                                                  877.739558   
median                                                     600.0   
mode           0    600.0
Name: trip_duration_seconds, dtype:...   
max                                                       6900.0   
min                                                        300.0   
std_dev                                               662.249972   
variance                                           438575.025548   
skewness                                                4.009658   
kurtosis                                               23.650188   
percentile_25                                              600.0   
percentile_75                                              900.0   
iqr                                                        300.0   
range                                                     6600.0   
cv                                                      0.754495   
qd                                                           0.2   
cs                                                      0.006055   
ck                                                      0.035712   
cvs                                                     0.006055   
cvk                                                     0.035712   
cvcs                                                    0.006055   
cvck                                                    0.035712   
cvcv                                                    0.754495   
cvqd                                                         0.2   
cvr                                                     7.519315   
cvm                                                          1.0   
cvmed                                                   0.683574   
cvmode         0    0.683574
Name: trip_duration_seconds, dty...   

column                                  trip_distance_kilometers  
rows                                                        2035  
sum                                                  3463.034938  
mean                                                    1.701737  
median                                                  1.299361  
mode           0        0.100246
1        0.101472
2        0...  
max                                                    13.561161  
min                                                     0.100246  
std_dev                                                 1.493913  
variance                                                2.231776  
skewness                                                2.338346  
kurtosis                                                9.186756  
percentile_25                                           0.697804  
percentile_75                                           2.227271  
iqr                                                     1.529467  
range                                                  13.460915  
cv                                                      0.877875  
qd                                                      0.522881  
cs                                                      1.565249  
ck                                                      6.149459  
cvs                                                     1.565249  
cvk                                                     6.149459  
cvcs                                                    1.565249  
cvck                                                    6.149459  
cvcv                                                    0.877875  
cvqd                                                    0.522881  
cvr                                                     7.910103  
cvm                                                          1.0  
cvmed                                                    0.76355  
cvmode         0

In [245]:
# get entries where trips start and end at station
evening_rush_nan_delay_tier_station_station = evening_rush_nan_delay_tier[evening_rush_nan_delay_tier['end_stop_id'].notna() & evening_rush_nan_delay_tier['start_stop_id'].notna()]
evening_rush_nan_delay_tier_station_station

tier_trips_id tier_trips_start_time tier_trips_end_time vehicle type  \
3035496      782304577   2023-07-01 17:10:00 2023-07-01 17:20:00    e-scooter   
3279241      782454774   2023-07-01 17:10:00 2023-07-01 17:25:00    e-scooter   
2954000      782279912   2023-07-01 17:15:00 2023-07-01 17:25:00    e-scooter   
3125894      782334920   2023-07-01 17:15:00 2023-07-01 17:25:00    e-scooter   
3200651      782382402   2023-07-01 17:20:00 2023-07-01 17:30:00    e-scooter   
...                ...                   ...                 ...          ...   
3485589      832265810   2023-07-31 19:20:00 2023-07-31 19:25:00    e-scooter   
3338036      832133400   2023-07-31 19:20:00 2023-07-31 19:30:00    e-scooter   
3485590      832265811   2023-07-31 19:25:00 2023-07-31 19:30:00    e-scooter   
3482367      832262713   2023-07-31 19:35:00 2023-07-31 19:45:00    e-scooter   
3402440      832186033   2023-07-31 19:45:00 2023-07-31 20:00:00    e-scooter   

          trip_duration  trip_distance_kilometers  trip_distance_meters  \
3035496 0 days 00:10:00                  1.576509           1576.508878   
3279241 0 days 00:15:00                  1.181511           1181.510808   
2954000 0 days 00:10:00                  1.327481           1327.480919   
3125894 0 days 00:10:00                  0.118998            118.997600   
3200651 0 days 00:10:00                  0.343392            343.391843   
...                 ...                       ...                   ...   
3485589 0 days 00:05:00                  0.182572            182.571976   
3338036 0 days 00:10:00                  0.968601            968.600969   
3485590 0 days 00:05:00                  0.212159            212.159418   
3482367 0 days 00:10:00                  0.600747            600.746929   
3402440 0 days 00:15:00                  0.621047            621.046655   

         start_stop_id         start_stop_name  \
3035496         1102.0      Bonn Friedensplatz   
3279241         1182.0      Bonn Chlodwigplatz   
2954000         1104.0          Bonn Stadthaus   
3125894          694.0  Bonn Tannenbusch Mitte   
3200651          687.0                Bonn Hbf   
...                ...                     ...   
3485589          686.0  Bonn Universität/Markt   
3338036         8471.0     Bonn Limperich Nord   
3485590         1103.0              Bonn Markt   
3482367         1405.0       Bonn Nordfriedhof   
3402440         1501.0      Bonn Beuel Rathaus   

                                         start_buffer_zone  end_stop_id  \
3035496  801621     POLYGON ((7.157885983913106 50.7227...       1192.0   
3279241  801621     POLYGON ((7.157885983913106 50.7227...       1184.0   
2954000  801621     POLYGON ((7.157885983913106 50.7227...        688.0   
3125894  801621     POLYGON ((7.157885983913106 50.7227...        694.0   
3200651  801621     POLYGON ((7.157885983913106 50.7227...       1144.0   
...                                                    ...          ...   
3485589  801621     POLYGON ((7.157885983913106 50.7227...       1103.0   
3338036  801621     POLYGON ((7.157885983913106 50.7227...       1504.0   
3485590  801621     POLYGON ((7.157885983913106 50.7227...        686.0   
3482367  801621     POLYGON ((7.157885983913106 50.7227...       8437.0   
3402440  801621     POLYGON ((7.157885983913106 50.7227...       1502.0   

                      end_stop_name  \
3035496              Bonn Ellerstr.   
3279241          Bonn Gerhardsplatz   
2954000                   Bonn West   
3125894      Bonn Tannenbusch Mitte   
3200651          Bonn Beethovenstr.   
...                             ...   
3485589                  Bonn Markt   
3338036               Bonn Beuel Bf   
3485590      Bonn Universität/Markt   
3482367      Bonn An Der Josefshöhe   
3402440  Bonn Beueler Bahnhofsplatz   

                                           end_buffer_zone  \
3035496  801621                                        ...   
3279241  801621                         

In [246]:
evening_rush_nan_delay_tier_station_station.describe()

tier_trips_id          tier_trips_start_time  \
count   8.170000e+02                            817   
mean    8.000746e+08  2023-07-15 17:00:15.789473792   
min     7.822649e+08            2023-07-01 17:10:00   
25%     7.823819e+08            2023-07-07 18:20:00   
50%     8.086424e+08            2023-07-14 17:05:00   
75%     8.087581e+08            2023-07-23 17:10:00   
max     8.323095e+08            2023-07-31 19:45:00   
std     1.763996e+07                            NaN   

                 tier_trips_end_time              trip_duration  \
count                            817                        817   
mean   2023-07-15 17:13:33.708690176  0 days 00:13:17.919216646   
min              2023-07-01 17:20:00            0 days 00:05:00   
25%              2023-07-07 18:30:00            0 days 00:10:00   
50%              2023-07-14 17:15:00            0 days 00:10:00   
75%              2023-07-23 17:30:00            0 days 00:15:00   
max              2023-07-31 20:00:00            0 days 01:55:00   
std                              NaN  0 days 00:10:53.447177707   

       trip_distance_kilometers  trip_distance_meters  start_stop_id  \
count                817.000000            817.000000     817.000000   
mean                   1.375616           1375.616489    1291.155447   
min                    0.100246            100.246164      43.000000   
25%                    0.569308            569.308432     694.000000   
50%                    1.095763           1095.762962    1115.000000   
75%                    1.782287           1782.287481    1240.000000   
max                    8.442163           8442.163487    9703.000000   
std                    1.164430           1164.430388    1174.258552   

       end_stop_id  trip_duration_seconds  
count   817.000000             817.000000  
mean   1448.922889             797.919217  
min      43.000000             300.000000  
25%    1106.000000             600.000000  
50%    1153.000000             600.000000  
75%    1244.000000             900.000000  
max    9703.000000            6900.000000  
std    1405.706494             653.447178

In [247]:
# get statistics for the tier trips that start and end at a station
get_stats(evening_rush_nan_delay_tier_station_station, ['trip_duration_seconds', 'trip_distance_kilometers'])

column                                     trip_duration_seconds  \
rows                                                         817   
sum                                                     651900.0   
mean                                                  797.919217   
median                                                     600.0   
mode           0    600.0
Name: trip_duration_seconds, dtype:...   
max                                                       6900.0   
min                                                        300.0   
std_dev                                               653.447178   
variance                                           426993.214054   
skewness                                                4.794424   
kurtosis                                               30.999595   
percentile_25                                              600.0   
percentile_75                                              900.0   
iqr                                                        300.0   
range                                                     6600.0   
cv                                                      0.818939   
qd                                                           0.2   
cs                                                      0.007337   
ck                                                       0.04744   
cvs                                                     0.007337   
cvk                                                      0.04744   
cvcs                                                    0.007337   
cvck                                                     0.04744   
cvcv                                                    0.818939   
cvqd                                                         0.2   
cvr                                                     8.271514   
cvm                                                          1.0   
cvmed                                                   0.751956   
cvmode         0    0.751956
Name: trip_duration_seconds, dty...   

column                                  trip_distance_kilometers  
rows                                                         817  
sum                                                  1123.878671  
mean                                                    1.375616  
median                                                  1.095763  
mode           0      0.100246
1      0.101712
2      0.10462...  
max                                                     8.442163  
min                                                     0.100246  
std_dev                                                  1.16443  
variance                                                1.355898  
skewness                                                1.793685  
kurtosis                                                4.278368  
percentile_25                                           0.569308  
percentile_75                                           1.782287  
iqr                                                     1.212979  
range                                                   8.341917  
cv                                                      0.846479  
qd                                                      0.515811  
cs                                                      1.540397  
ck                                                      3.674216  
cvs                                                     1.540397  
cvk                                                     3.674216  
cvcs                                                    1.540397  
cvck                                                    3.674216  
cvcv                                                    0.846479  
cvqd                                                    0.515811  
cvr                                                      6.06413  
cvm                                                          1.0  
cvmed                                                   0.796561  
cvmode         0

In [248]:
evening_rush_nan_delay_next = check_micromobility_datasets('next', evening_rush_nan_delay)

In [249]:
evening_rush_nan_delay_next.describe()

nextbike_trips_id      nextbike_trips_start_time  \
count       4.681000e+03                           4681   
mean        3.793736e+07  2023-07-15 23:28:20.995513600   
min         3.771661e+07            2023-07-01 17:01:00   
25%         3.782177e+07            2023-07-07 18:01:00   
50%         3.793640e+07            2023-07-14 19:16:00   
75%         3.805075e+07            2023-07-23 17:21:00   
max         3.817174e+07            2023-07-31 19:56:00   
std         1.300633e+05                            NaN   

             nextbike_trips_end_time              trip_duration  \
count                           4681                       4681   
mean   2023-07-15 23:43:18.688314624  0 days 00:14:57.692800683   
min              2023-07-01 17:11:00            0 days 00:05:00   
25%              2023-07-07 18:21:00            0 days 00:10:00   
50%              2023-07-14 19:36:00            0 days 00:15:00   
75%              2023-07-23 17:36:00            0 days 00:15:00   
max              2023-07-31 20:11:00            0 days 02:00:00   
std                              NaN  0 days 00:09:31.464433513   

       trip_distance_kilometers  trip_distance_meters  start_stop_id  \
count               4681.000000           4681.000000    3660.000000   
mean                   1.680010           1680.009647    1248.829508   
min                    0.100057            100.057033      43.000000   
25%                    0.769639            769.638877     692.000000   
50%                    1.293174           1293.174425    1115.000000   
75%                    2.122992           2122.991658    1223.000000   
max                   12.651486          12651.485598    9780.000000   
std                    1.388564           1388.563831    1183.325911   

       end_stop_id  trip_duration_seconds  
count  2601.000000            4681.000000  
mean   1353.682430             897.692801  
min      43.000000             300.000000  
25%    1104.000000             600.000000  
50%    1153.000000             900.000000  
75%    1224.000000             900.000000  
max    9780.000000            7200.000000  
std    1288.149059             571.464434

In [250]:
get_stats(evening_rush_nan_delay_next, ['trip_duration_seconds', 'trip_distance_kilometers'])

column                                     trip_duration_seconds  \
rows                                                        4681   
sum                                                    4202100.0   
mean                                                  897.692801   
median                                                     900.0   
mode           0    600.0
Name: trip_duration_seconds, dtype:...   
max                                                       7200.0   
min                                                        300.0   
std_dev                                               571.464434   
variance                                           326571.598771   
skewness                                                3.442401   
kurtosis                                               21.115277   
percentile_25                                              600.0   
percentile_75                                              900.0   
iqr                                                        300.0   
range                                                     6900.0   
cv                                                      0.636592   
qd                                                           0.2   
cs                                                      0.006024   
ck                                                      0.036949   
cvs                                                     0.006024   
cvk                                                     0.036949   
cvcs                                                    0.006024   
cvck                                                    0.036949   
cvcv                                                    0.636592   
cvqd                                                         0.2   
cvr                                                     7.686371   
cvm                                                          1.0   
cvmed                                                    1.00257   
cvmode         0    0.66838
Name: trip_duration_seconds, dtyp...   

column                                  trip_distance_kilometers  
rows                                                        4681  
sum                                                  7864.125158  
mean                                                     1.68001  
median                                                  1.293174  
mode           0    0.376674
1    0.441151
2    0.718744
3   ...  
max                                                    12.651486  
min                                                     0.100057  
std_dev                                                 1.388564  
variance                                                 1.92811  
skewness                                                2.076476  
kurtosis                                                6.363973  
percentile_25                                           0.769639  
percentile_75                                           2.122992  
iqr                                                     1.353353  
range                                                  12.551429  
cv                                                      0.826521  
qd                                                      0.467862  
cs                                                      1.495413  
ck                                                      4.583133  
cvs                                                     1.495413  
cvk                                                     4.583133  
cvcs                                                    1.495413  
cvck                                                    4.583133  
cvcv                                                    0.826521  
cvqd                                                    0.467862  
cvr                                                     7.471046  
cvm                                                          1.0  
cvmed                                                   0.769742  
cvmode         0

In [251]:
# get entries where trips start and end at station
evening_rush_nan_delay_next_station_station = evening_rush_nan_delay_next[evening_rush_nan_delay_next['end_stop_id'].notna() & evening_rush_nan_delay_next['start_stop_id'].notna()]
evening_rush_nan_delay_next_station_station

nextbike_trips_id nextbike_trips_start_time nextbike_trips_end_time  \
1505010           38062285       2023-07-01 17:01:00     2023-07-01 17:16:00   
1574793           37748052       2023-07-01 17:06:00     2023-07-01 17:16:00   
1555237           38113591       2023-07-01 17:06:00     2023-07-01 17:26:00   
1287486           37872114       2023-07-01 17:06:00     2023-07-01 17:16:00   
1668989           37800408       2023-07-01 17:06:00     2023-07-01 17:16:00   
...                    ...                       ...                     ...   
1290123           37839777       2023-07-31 19:21:00     2023-07-31 19:31:00   
1539402           38089360       2023-07-31 19:31:00     2023-07-31 19:41:00   
1528561           38080605       2023-07-31 19:36:00     2023-07-31 19:51:00   
1377018           37916580       2023-07-31 19:41:00     2023-07-31 19:51:00   
1385653           37921677       2023-07-31 19:51:00     2023-07-31 19:56:00   

         nextbike_trips_start_at_station  nextbike_trips_end_at_station  \
1505010                            False                          False   
1574793                            False                          False   
1555237                            False                          False   
1287486                            False                          False   
1668989                             True                          False   
...                                  ...                            ...   
1290123                            False                          False   
1539402                            False                           True   
1528561                             True                          False   
1377018                            False                          False   
1385653                            False                          False   

        vehicle type   trip_duration  trip_distance_kilometers  \
1505010         bike 0 days 00:15:00                  0.963955   
1574793         bike 0 days 00:10:00                  1.046114   
1555237         bike 0 days 00:20:00                  1.766626   
1287486         bike 0 days 00:10:00                  0.148911   
1668989         bike 0 days 00:10:00                  1.313219   
...              ...             ...                       ...   
1290123         bike 0 days 00:10:00                  1.040513   
1539402         bike 0 days 00:10:00                  0.814886   
1528561         bike 0 days 00:15:00                  1.272803   
1377018         bike 0 days 00:10:00                  0.736360   
1385653         bike 0 days 00:05:00                  0.161536   

         trip_distance_meters  \
1505010            963.954661   
1574793           1046.114110   
1555237           1766.626256   
1287486            148.911114   
1668989           1313.218705   
...                       ...   
1290123           1040.512967   
1539402            814.886181   
1528561           1272.802661   
1377018            736.359754   
1385653            161.535610   

                                            start_location  \
1505010  b'\x01\x01\x00\x00\x00\xbd\xab\x1e0\x0fY\x1c@\...   
1574793  b'\x01\x01\x00\x00\x00`vO\x1e\x16j\x1c@m\xff\x...   
1555237  b'\x01\x01\x00\x00\x00u\xc7b\x9bTd\x1c@=\xd5!7...   
1287486  b'\x01\x01\x00\x00\x00\xea<*\xfe\xefh\x1c@uYLl...   
1668989  b'\x01\x01\x00\x00\x00\xa6}s\x7f\xf5h\x1c@\x92...   
...                                                    ...   
1290123  b'\x01\x01\x00\x00\x00{/\xbeh\x8fg\x1c@\xac\x8...   
1539402  b'\x01\x01\x00\x00\x00/\xc3\x7f\xba\x81b\x1c@h...   
1528561  b'\x01\x01\x00\x00\x00&\x199\x0b{Z\x1c@\xb4\xe...   
1377018  b'\x01\x01\x00\x00\x00\xcd\xc8 w\x11v\x1c@l\xb...   
1385653  b'\x01\x01\x00\x00\x00\xb6/\xa0\x17\xee\\\x1c@...   

                                              end_location  start_stop_id  \
1505010  b'\x01\x01\x00\x00\x00E\xba\x9fS\x90_\x1c@4\x9...         1140.0   
1574793  b'\x01\x01\x00\x00\x007n1?7d\x1c@l\x94\xf5\x9b...

In [252]:
evening_rush_nan_delay_next_station_station.describe()

nextbike_trips_id      nextbike_trips_start_time  \
count       2.219000e+03                           2219   
mean        3.793669e+07  2023-07-15 20:24:35.908066560   
min         3.771661e+07            2023-07-01 17:01:00   
25%         3.781651e+07            2023-07-07 18:31:00   
50%         3.793757e+07            2023-07-14 18:16:00   
75%         3.805224e+07            2023-07-22 19:16:00   
max         3.817174e+07            2023-07-31 19:51:00   
std         1.309537e+05                            NaN   

             nextbike_trips_end_time              trip_duration  \
count                           2219                       2219   
mean   2023-07-15 20:38:31.689950208  0 days 00:13:55.781883731   
min              2023-07-01 17:16:00            0 days 00:05:00   
25%              2023-07-07 18:46:00            0 days 00:10:00   
50%              2023-07-14 18:31:00            0 days 00:10:00   
75%              2023-07-22 19:31:00            0 days 00:15:00   
max              2023-07-31 19:56:00            0 days 02:00:00   
std                              NaN  0 days 00:08:38.807207968   

       trip_distance_kilometers  trip_distance_meters  start_stop_id  \
count               2219.000000           2219.000000    2219.000000   
mean                   1.417859           1417.858676    1285.071654   
min                    0.100057            100.057033      43.000000   
25%                    0.721985            721.984587     694.000000   
50%                    1.173018           1173.017828    1133.000000   
75%                    1.798070           1798.069539    1221.000000   
max                    9.110475           9110.475451    9780.000000   
std                    1.099769           1099.769342    1230.320481   

       end_stop_id  trip_duration_seconds  
count  2219.000000            2219.000000  
mean   1379.933303             835.781884  
min      43.000000             300.000000  
25%    1106.000000             600.000000  
50%    1153.000000             600.000000  
75%    1224.000000             900.000000  
max    9780.000000            7200.000000  
std    1330.222487             518.807208

In [253]:
# get statistics for the tier trips that start and end at a station
get_stats(evening_rush_nan_delay_next_station_station, ['trip_duration_seconds', 'trip_distance_kilometers'])

column                                     trip_duration_seconds  \
rows                                                        2219   
sum                                                    1854600.0   
mean                                                  835.781884   
median                                                     600.0   
mode           0    600.0
Name: trip_duration_seconds, dtype:...   
max                                                       7200.0   
min                                                        300.0   
std_dev                                               518.807208   
variance                                            269160.91904   
skewness                                                3.776843   
kurtosis                                               27.562569   
percentile_25                                              600.0   
percentile_75                                              900.0   
iqr                                                        300.0   
range                                                     6900.0   
cv                                                      0.620745   
qd                                                           0.2   
cs                                                       0.00728   
ck                                                      0.053127   
cvs                                                      0.00728   
cvk                                                     0.053127   
cvcs                                                     0.00728   
cvck                                                    0.053127   
cvcv                                                    0.620745   
cvqd                                                         0.2   
cvr                                                     8.255742   
cvm                                                          1.0   
cvmed                                                   0.717891   
cvmode         0    0.717891
Name: trip_duration_seconds, dty...   

column                                  trip_distance_kilometers  
rows                                                        2219  
sum                                                  3146.228402  
mean                                                    1.417859  
median                                                  1.173018  
mode           0    0.441151
1    0.718744
Name: trip_distanc...  
max                                                     9.110475  
min                                                     0.100057  
std_dev                                                 1.099769  
variance                                                1.209493  
skewness                                                2.121464  
kurtosis                                                6.817808  
percentile_25                                           0.721985  
percentile_75                                            1.79807  
iqr                                                     1.076085  
range                                                   9.010418  
cv                                                      0.775655  
qd                                                      0.427009  
cs                                                      1.929008  
ck                                                      6.199307  
cvs                                                     1.929008  
cvk                                                     6.199307  
cvcs                                                    1.929008  
cvck                                                    6.199307  
cvcv                                                    0.775655  
cvqd                                                    0.427009  
cvr                                                     6.354948  
cvm                                                          1.0  
cvmed                                                   0.827316  
cvmode         0

In [254]:
evening_rush_delay.describe()

route_id      agency_id     route_type    service_id  \
count  173541.000000  173541.000000  173541.000000  173541.00000   
mean      568.607436       6.004633       2.777188    2627.51041   
min        60.000000       6.000000       0.000000      43.00000   
25%       602.000000       6.000000       3.000000      64.00000   
50%       607.000000       6.000000       3.000000      64.00000   
75%       611.000000       6.000000       3.000000     130.00000   
max       843.000000      12.000000       3.000000   27690.00000   
std       145.979368       0.159453       0.786635    7859.54371   

        direction_id       shape_id        stop_id  \
count  173541.000000  173541.000000  173541.000000   
mean        0.514426    3622.426199    2315.174478   
min         0.000000       6.000000      43.000000   
25%         0.000000    1915.000000    1221.000000   
50%         1.000000    2717.000000    1441.000000   
75%         1.000000    5633.000000    1681.000000   
max         1.000000   10365.000000    9780.000000   
std         0.499793    2810.575546    2404.570599   

                 actual_arrival_time          actual_departure_time  \
count                         168578                         173541   
mean   2023-07-17 00:13:35.945645568  2023-07-17 00:45:02.498487296   
min              2023-07-01 17:00:00            2023-07-01 17:00:15   
25%              2023-07-09 18:39:00            2023-07-09 18:36:45   
50%              2023-07-17 18:54:30            2023-07-17 19:00:30   
75%              2023-07-24 17:56:00            2023-07-24 18:04:45   
max              2023-07-31 20:11:45            2023-07-31 20:12:00   
std                              NaN                            NaN   

       vrs_timestamp  ...  departure_delay_float actual_arrival_time_float  \
count  173541.000000  ...          173541.000000             173541.000000   
mean   175765.903337  ...               0.647135             178181.911623   
min    150304.000000  ...               0.166667                  0.000000   
25%    163805.000000  ...               0.250000             174430.000000   
50%    172804.000000  ...               0.500000             183130.000000   
75%    181304.000000  ...               0.750000             191515.000000   
max    220309.000000  ...              24.000000             201145.000000   
std     18012.564138  ...               1.188004              31643.026883   

      actual_departure_time_float arrival_delay_span    weather_int  \
count               173541.000000           173541.0  173541.000000   
mean                183472.905942                0.0       0.162019   
min                 170010.000000                0.0       0.000000   
25%                 174930.000000                0.0       0.000000   
50%                 183440.000000                0.0       0.000000   
75%                 191715.000000                0.0       0.000000   
max                 201200.000000                0.0       2.000000   
std                   8288.686486                0.0       0.429383   

       time_span_int_arrival        weekend  time_span_int  delay_category  \
count          173541.000000  173541.000000  173541.000000   173541.000000   
mean                4.857561       0.710218       5.001325        0.640759   
min                 0.000000       0.000000       5.000000       -1.000000   
25%                 5.000000       0.000000       5.000000        0.000000   
50%                 5.000000       0.000000       5.000000        1.000000   
75%                 5.000000       1.000000       5.000000        1.000000   
max                 6.000000       3.000000       6.000000        1.000000   
std                 0.834080       1.026508       0.036381        0.536083   

       cancelled_trip  
count        173541.0  
mean              0.0  
min               0.0  
25%               0.0  
50%               0.0  
75%               0.0  
max               0.0  
std               0.0  

[8 rows x

In [255]:
evening_rush_no_delay.describe()

route_id      agency_id     route_type     service_id  \
count  105539.000000  105539.000000  105539.000000  105539.000000   
mean      571.217370       7.007372       2.664437    5208.801855   
min        16.000000       1.000000       0.000000      43.000000   
25%       600.000000       6.000000       3.000000      64.000000   
50%       607.000000       6.000000       3.000000      64.000000   
75%       630.000000       6.000000       3.000000     151.000000   
max       884.000000      12.000000       3.000000   29145.000000   
std       204.688942       2.102732       0.945566   10643.247332   

        direction_id      shape_id        stop_id  \
count  105539.000000  105539.00000  105539.000000   
mean        0.504667    4220.88735    2217.953771   
min         0.000000       6.00000      43.000000   
25%         0.000000    2014.00000    1182.000000   
50%         1.000000    3858.00000    1433.000000   
75%         1.000000    6377.00000    1711.000000   
max         1.000000   10365.00000    9780.000000   
std         0.499981    2858.41660    2331.080980   

                 actual_arrival_time          actual_departure_time  \
count                          75680                         105539   
mean   2023-07-16 23:09:56.840512512  2023-07-16 23:24:20.838836992   
min              2023-07-01 16:59:00            2023-07-01 17:00:00   
25%              2023-07-09 17:53:40            2023-07-09 17:45:00   
50%       2023-07-17 18:51:42.500000            2023-07-17 18:44:00   
75%       2023-07-24 17:51:32.500000            2023-07-24 18:02:00   
max              2023-07-31 20:02:00            2023-07-31 20:02:00   
std                              NaN                            NaN   

       vrs_timestamp  ...  departure_delay_float actual_arrival_time_float  \
count  105539.000000  ...          105539.000000             105539.000000   
mean   175396.102237  ...               0.040939             131468.493827   
min    150304.000000  ...               0.000000                  0.000000   
25%    163804.000000  ...               0.000000                  0.000000   
50%    172804.000000  ...               0.000000             175845.000000   
75%    181304.000000  ...               0.000000             185945.000000   
max    220309.000000  ...              24.000000             200200.000000   
std     17532.513109  ...               0.435419              82880.078353   

      actual_departure_time_float arrival_delay_span    weather_int  \
count               105539.000000           105539.0  105539.000000   
mean                183451.566056                0.0       0.157070   
min                 170000.000000                0.0       0.000000   
25%                 174800.000000                0.0       0.000000   
50%                 183400.000000                0.0       0.000000   
75%                 191800.000000                0.0       0.000000   
max                 201200.000000                0.0       2.000000   
std                   8371.373825                0.0       0.421288   

       time_span_int_arrival        weekend  time_span_int  delay_category  \
count          105539.000000  105539.000000  105539.000000   105539.000000   
mean                3.581937       0.736941       5.000322       -0.276211   
min                 0.000000       0.000000       5.000000       -1.000000   
25%                 0.000000       0.000000       5.000000       -1.000000   
50%                 5.000000       0.000000       5.000000        0.000000   
75%                 5.000000       2.000000       5.000000        0.000000   
max                 6.000000       3.000000       6.000000        1.000000   
std                 2.250703       1.027220       0.017946        0.461884   

       cancelled_trip  
count        105539.0  
mean              0.0  
min               0.0  
25%               0.0  
50%               0.0  
75%               0.0  
max               0.0  
std               0.0  

[8 rows x

In [256]:
evening_rush_nan_delay.describe()

route_id      agency_id     route_type     service_id  \
count  171041.000000  171041.000000  171041.000000  171041.000000   
mean      555.394215       6.303898       2.678533    3906.452435   
min        16.000000       1.000000       0.000000      43.000000   
25%       601.000000       6.000000       3.000000      64.000000   
50%       607.000000       6.000000       3.000000      64.000000   
75%       613.000000       6.000000       3.000000     130.000000   
max       884.000000      12.000000       3.000000   28777.000000   
std       180.874761       1.215888       0.927936    9386.116269   

        direction_id       shape_id        stop_id actual_arrival_time  \
count  171041.000000  171041.000000  171041.000000                   0   
mean        0.494905    4090.735356    2268.328459                 NaT   
min         0.000000       6.000000      43.000000                 NaT   
25%         0.000000    1975.000000    1221.000000                 NaT   
50%         0.000000    2952.000000    1468.000000                 NaT   
75%         1.000000    6327.000000    1687.000000                 NaT   
max         1.000000   10365.000000    9780.000000                 NaT   
std         0.499975    2936.477714    2352.239184                 NaN   

      actual_departure_time  vrs_timestamp  ...  departure_delay_float  \
count                     0  171041.000000  ...                    0.0   
mean                    NaT  168484.487369  ...                    NaN   
min                     NaT  123304.000000  ...                    NaN   
25%                     NaT  162304.000000  ...                    NaN   
50%                     NaT  165804.000000  ...                    NaN   
75%                     NaT  174804.000000  ...                    NaN   
max                     NaT  220309.000000  ...                    NaN   
std                     NaN   10820.756595  ...                    NaN   

      actual_arrival_time_float actual_departure_time_float  \
count                  171041.0                    171041.0   
mean                        0.0                         0.0   
min                         0.0                         0.0   
25%                         0.0                         0.0   
50%                         0.0                         0.0   
75%                         0.0                         0.0   
max                         0.0                         0.0   
std                         0.0                         0.0   

      arrival_delay_span    weather_int  time_span_int_arrival        weekend  \
count           171041.0  171041.000000               171041.0  171041.000000   
mean                 0.0       0.149730                    0.0       0.749627   
min                  0.0       0.000000                    0.0       0.000000   
25%                  0.0       0.000000                    0.0       0.000000   
50%                  0.0       0.000000                    0.0       0.000000   
75%                  0.0       0.000000                    0.0       2.000000   
max                  0.0       2.000000                    0.0       3.000000   
std                  0.0       0.377633                    0.0       0.999123   

       time_span_int  delay_category  cancelled_trip  
count       171041.0        171041.0        171041.0  
mean             0.0            -1.0             1.0  
min              0.0            -1.0             1.0  
25%              0.0            -1.0             1.0  
50%              0.0            -1.0             1.0  
75%              0.0            -1.0             1.0  
max              0.0            -1.0             1.0  
std              0.0             0.0             0.0  

[8 rows x 38 columns]

#### Evening

In [257]:
evening_delay = delay[(delay['scheduled_arrival_time'].dt.hour > 19) & (delay['scheduled_arrival_time'].dt.hour < 22)]
evening_delay

route_id  agency_id route_short_name  route_type route_type_name  \
70818         604          6              604           3             Bus   
70820         602          6              602           3             Bus   
70821         600          6              600           3             Bus   
70822         639          6              639           3             Bus   
70823         611          6              611           3             Bus   
...           ...        ...              ...         ...             ...   
2557453       604          6              604           3             Bus   
2557455       606          6              606           3             Bus   
2557460       606          6              606           3             Bus   
2557462       600          6              600           3             Bus   
2557464       610          6              610           3             Bus   

                               agency_name  service_id  \
70818    SWB Stadtwerke Bonn Verkehrs GmbH         130   
70820    SWB Stadtwerke Bonn Verkehrs GmbH         130   
70821    SWB Stadtwerke Bonn Verkehrs GmbH         130   
70822    SWB Stadtwerke Bonn Verkehrs GmbH         130   
70823    SWB Stadtwerke Bonn Verkehrs GmbH         130   
...                                    ...         ...   
2557453  SWB Stadtwerke Bonn Verkehrs GmbH          43   
2557455  SWB Stadtwerke Bonn Verkehrs GmbH          43   
2557460  SWB Stadtwerke Bonn Verkehrs GmbH           3   
2557462  SWB Stadtwerke Bonn Verkehrs GmbH          64   
2557464  SWB Stadtwerke Bonn Verkehrs GmbH          43   

                                                   trip_id  \
70818    6040181-604-006-1382.2.21:195800-49-1_094128CD...   
70820    6020212-602-006-9478.2.22:191800-39-1_9621447A...   
70821    6000390-600-006-8813.2.22:195900-32-1_65A058DE...   
70822    6390195-639-006-1680.2.21:194800-17-1_C9E68010...   
70823    6110399-611-006-1723.2.21:192600-60-1_2DF8F913...   
...                                                    ...   
2557453  6040010-604-006-678.2.21:212200-51-1_9FBDFFD5-...   
2557455  6060040-606-006-1584.2.22:211000-44-1_CD3EBE21...   
2557460  6060039-606-006-1357.2.21:213800-42-1_294F6A18...   
2557462  6000110-600-006-8813.2.22:214300-32-1_07F1D6C7...   
2557464  6100026-610-006-1341.2.24:215100-53-1_B2803993...   

                     trip_headsign  direction_id  ...  delay_span  \
70818                       Hersel             0  ...         0-5   
70820                       Waldau             1  ...         0-5   
70821          Ippendorf Altenheim             1  ...         0-5   
70822    Stadtwald/Ev. Krankenhaus             0  ...         0-5   
70823         Lessenich Sportplatz             0  ...         0-5   
...                            ...           ...  ...         ...   
2557453            Ückesdorf Mitte             1  ...         0-5   
2557455         Hardtberg Klinikum             1  ...         0-5   
2557460                 Ramersdorf             0  ...         0-5   
2557462        Ippendorf Altenheim             1  ...         0-5   
2557464               Giselherstr.             1  ...         0-5   

         arrival_delay_span weather_int time_span_arrival  \
70818                     0           0           evening   
70820                     0           0           evening   
70821                     0           0           evening   
70822                     0           0           evening   
70823                     0           0           evening   
...                     ...         ...               ...   
2557453                   0           1           evening   
2557455                   0           1           evening   
2557460                   0           1           evening   
2557462                   0           1           evening   
2557464                   0           1           evening   

         time_span_int_arrival  weekend time_span time_span_int  \
70818        

In [258]:
get_stats(evening_delay, ['tier_trips_count', 'tier_trips_end_at_station_count', 'nextbike_trips_count', 'nextbike_trips_end_at_station_count', 'current_temp', 'current_precipitation_volume'])

/tmp/ipykernel_2575952/41814695.py:51: RuntimeWarning: invalid value encountered in scalar divide
  qd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:55: RuntimeWarning: invalid value encountered in scalar divide
  cvqd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:51: RuntimeWarning: invalid value encountered in scalar divide
  qd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:55: RuntimeWarning: invalid value encountered in scalar divide
  cvqd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:51: RuntimeWarning: invalid value encountered in scalar divide
  qd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:55: RuntimeWarning: invalid value encountered in scalar divide
  cvqd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:51: RuntimeWarning: invalid value encountered in scalar divide
  qd = iqr / (percentile_75 + percenti

column                                        tier_trips_count  \
rows                                                     82723   
sum                                                       1039   
mean                                                   0.01256   
median                                                     0.0   
mode               0    0
Name: tier_trips_count, dtype: int64   
max                                                          5   
min                                                          0   
std_dev                                               0.126031   
variance                                              0.015884   
skewness                                             12.822404   
kurtosis                                            228.493403   
percentile_25                                              0.0   
percentile_75                                              0.0   
iqr                                                        0.0   
range                                                        5   
cv                                                    10.03436   
qd                                                         NaN   
cs                                                  101.739714   
ck                                                 1812.987168   
cvs                                                 101.739714   
cvk                                                1812.987168   
cvcs                                                101.739714   
cvck                                               1812.987168   
cvcv                                                  10.03436   
cvqd                                                       NaN   
cvr                                                 398.089509   
cvm                                                        1.0   
cvmed                                                      0.0   
cvmode         0    0.0
Name: tier_trips_count, dtype: float64   

column                           tier_trips_end_at_station_count  \
rows                                                       82723   
sum                                                          854   
mean                                                    0.010324   
median                                                       0.0   
mode           0    0
Name: tier_trips_end_at_station_count, ...   
max                                                            5   
min                                                            0   
std_dev                                                 0.114324   
variance                                                 0.01307   
skewness                                               14.404401   
kurtosis                                               294.78793   
percentile_25                                                0.0   
percentile_75                                                0.0   
iqr                                                          0.0   
range                                                          5   
cv                                                     11.074079   
qd                                                           NaN   
cs                                                    125.995779   
ck                                                   2578.519849   
cvs                                                   125.995779   
cvk                                                  2578.519849   
cvcs                                                  125.995779   
cvck                                                 2578.519849   
cvcv                                                   11.074079   
cvqd                                                         NaN   
cvr                                                   484.326698   
cvm                                                          1.0   
cvmed                                                        0.0   
cvmode         0    0.0
Name: tier_trips_end_at

In [259]:
evening_delay_tier = check_micromobility_datasets('tier', evening_delay)

In [260]:
evening_delay_tier.describe()

tier_trips_id          tier_trips_start_time  \
count   7.630000e+02                            763   
mean    8.000945e+08  2023-07-15 23:46:19.423328768   
min     7.822645e+08            2023-07-01 20:05:00   
25%     7.823796e+08            2023-07-08 20:32:30   
50%     8.086397e+08            2023-07-14 21:10:00   
75%     8.087665e+08            2023-07-22 20:22:30   
max     8.323071e+08            2023-07-31 21:40:00   
std     1.702950e+07                            NaN   

                 tier_trips_end_time              trip_duration  \
count                            763                        763   
mean   2023-07-16 00:02:12.581913600  0 days 00:15:53.158584534   
min              2023-07-01 20:15:00            0 days 00:05:00   
25%              2023-07-08 20:55:00            0 days 00:10:00   
50%              2023-07-14 21:35:00            0 days 00:15:00   
75%              2023-07-22 20:42:30            0 days 00:20:00   
max              2023-07-31 22:00:00            0 days 01:55:00   
std                              NaN  0 days 00:12:46.186219261   

       trip_distance_kilometers  trip_distance_meters  start_stop_id  \
count                763.000000            763.000000     521.000000   
mean                   1.923551           1923.550841    1386.598848   
min                    0.101898            101.897626     161.000000   
25%                    0.846107            846.107312    1103.000000   
50%                    1.462686           1462.685671    1115.000000   
75%                    2.474115           2474.115355    1244.000000   
max                    9.797339           9797.338871    9702.000000   
std                    1.527522           1527.521893    1315.091536   

       end_stop_id  trip_duration_seconds  
count   414.000000             763.000000  
mean   1601.632850             953.158585  
min     161.000000             300.000000  
25%    1110.000000             600.000000  
50%    1162.000000             900.000000  
75%    1312.000000            1200.000000  
max    9703.000000            6900.000000  
std    1795.982923             766.186219

In [261]:
get_stats(evening_delay_tier, ['trip_duration_seconds', 'trip_distance_kilometers'])

column                                     trip_duration_seconds  \
rows                                                         763   
sum                                                     727260.0   
mean                                                  953.158585   
median                                                     900.0   
mode           0    600.0
Name: trip_duration_seconds, dtype:...   
max                                                       6900.0   
min                                                        300.0   
std_dev                                               766.186219   
variance                                           587041.322587   
skewness                                                4.276479   
kurtosis                                               23.813487   
percentile_25                                              600.0   
percentile_75                                             1200.0   
iqr                                                        600.0   
range                                                     6600.0   
cv                                                      0.803839   
qd                                                      0.333333   
cs                                                      0.005582   
ck                                                      0.031081   
cvs                                                     0.005582   
cvk                                                     0.031081   
cvcs                                                    0.005582   
cvck                                                    0.031081   
cvcv                                                    0.803839   
cvqd                                                    0.333333   
cvr                                                     6.924346   
cvm                                                          1.0   
cvmed                                                   0.944229   
cvmode         0    0.629486
Name: trip_duration_seconds, dty...   

column                                  trip_distance_kilometers  
rows                                                         763  
sum                                                  1467.669292  
mean                                                    1.923551  
median                                                  1.462686  
mode           0      0.101898
1      0.106632
2      0.10985...  
max                                                     9.797339  
min                                                     0.101898  
std_dev                                                 1.527522  
variance                                                2.333323  
skewness                                                1.540978  
kurtosis                                                2.761617  
percentile_25                                           0.846107  
percentile_75                                           2.474115  
iqr                                                     1.628008  
range                                                   9.695441  
cv                                                      0.794116  
qd                                                      0.490331  
cs                                                      1.008809  
ck                                                      1.807906  
cvs                                                     1.008809  
cvk                                                     1.807906  
cvcs                                                    1.008809  
cvck                                                    1.807906  
cvcv                                                    0.794116  
cvqd                                                    0.490331  
cvr                                                     5.040387  
cvm                                                          1.0  
cvmed                                                   0.760409  
cvmode         0

In [262]:
# get entries where trips start and end at station
evening_delay_tier_station_station = evening_delay_tier[evening_delay_tier['end_stop_id'].notna() & evening_delay_tier['start_stop_id'].notna()]
evening_delay_tier_station_station

tier_trips_id tier_trips_start_time tier_trips_end_time vehicle type  \
3258480      782435847   2023-07-01 20:05:00 2023-07-01 20:15:00    e-scooter   
2963101      782283108   2023-07-01 20:10:00 2023-07-01 20:25:00    e-scooter   
3038281      782305382   2023-07-01 20:55:00 2023-07-01 21:40:00    e-scooter   
3232393      782412139   2023-07-01 20:55:00 2023-07-01 21:10:00    e-scooter   
3278921      782454505   2023-07-01 21:00:00 2023-07-01 21:15:00    e-scooter   
...                ...                   ...                 ...          ...   
3397516      832181337   2023-07-31 20:25:00 2023-07-31 20:40:00    e-scooter   
3385595      832169884   2023-07-31 21:00:00 2023-07-31 21:10:00    e-scooter   
3416889      832199855   2023-07-31 21:10:00 2023-07-31 21:15:00    e-scooter   
3470811      832251610   2023-07-31 21:15:00 2023-07-31 21:25:00    e-scooter   
3507061      832286394   2023-07-31 21:40:00 2023-07-31 22:00:00    e-scooter   

          trip_duration  trip_distance_kilometers  trip_distance_meters  \
3258480 0 days 00:10:00                  1.683868           1683.868403   
2963101 0 days 00:15:00                  0.325097            325.096903   
3038281 0 days 00:45:00                  0.459868            459.867527   
3232393 0 days 00:15:00                  1.902178           1902.177877   
3278921 0 days 00:15:00                  1.816617           1816.616534   
...                 ...                       ...                   ...   
3397516 0 days 00:15:00                  1.826075           1826.075311   
3385595 0 days 00:10:00                  0.287767            287.767278   
3416889 0 days 00:05:00                  0.960512            960.511916   
3470811 0 days 00:10:00                  1.001662           1001.661564   
3507061 0 days 00:20:00                  2.090062           2090.062070   

         start_stop_id                            start_stop_name  \
3258480         1221.0                          Bonn Kaufmannstr.   
2963101         1110.0                         Bonn Wilhelmsplatz   
3038281         1102.0                         Bonn Friedensplatz   
3232393         2667.0  Bonn Brüdergasse/Bertha-Von-Suttner-Platz   
3278921         1268.0                              Bonn Rheinaue   
...                ...                                        ...   
3397516         1290.0                           Bonn Casselsruhe   
3385595         1115.0  Bonn Bertha-Von-Suttner-Pl./Beethovenhaus   
3416889         1500.0                 Bonn Konrad-Adenauer-Platz   
3470811         1223.0                            Bonn Beringstr.   
3507061         1110.0                         Bonn Wilhelmsplatz   

                                         start_buffer_zone  end_stop_id  \
3258480  801621     POLYGON ((7.157885983913106 50.7227...       1190.0   
2963101  801621     POLYGON ((7.157885983913106 50.7227...       1162.0   
3038281  801621     POLYGON ((7.157885983913106 50.7227...       1162.0   
3232393  801621     POLYGON ((7.157885983913106 50.7227...       1510.0   
3278921  801621     POLYGON ((7.157885983913106 50.7227...       1585.0   
...                                                    ...          ...   
3397516  801621     POLYGON ((7.157885983913106 50.7227...       1302.0   
3385595  801621     POLYGON ((7.157885983913106 50.7227...       1111.0   
3416889  801621     POLYGON ((7.157885983913106 50.7227...       1504.0   
3470811  801621     POLYGON ((7.157885983913106 50.7227...       1131.0   
3507061  801621     POLYGON ((7.157885983913106 50.7227...       1184.0   

                        end_stop_name  \
3258480                Bonn Zeisigweg   
2963101                 Bonn Rosental   
3038281                 Bonn Rosental   
3232393  Bonn Schwarzrheindorf Kirche   
3278921              Bonn Küdinghoven   
...                               ...   
3397516        Bonn Ippendorfer Allee   
3385595   Bonn Beethovenhalle Und Swb   
3416889                 Bonn Beuel B

In [263]:
evening_delay_tier_station_station.describe()

tier_trips_id          tier_trips_start_time  \
count   3.370000e+02                            337   
mean    8.015460e+08  2023-07-16 23:29:48.427299584   
min     7.822658e+08            2023-07-01 20:05:00   
25%     7.823956e+08            2023-07-10 20:00:00   
50%     8.086610e+08            2023-07-15 21:45:00   
75%     8.087816e+08            2023-07-22 21:55:00   
max     8.323050e+08            2023-07-31 21:40:00   
std     1.707410e+07                            NaN   

                 tier_trips_end_time              trip_duration  \
count                            337                        337   
mean   2023-07-16 23:44:28.842729728  0 days 00:14:40.415430267   
min              2023-07-01 20:15:00            0 days 00:05:00   
25%              2023-07-10 20:25:00            0 days 00:10:00   
50%              2023-07-15 21:55:00            0 days 00:10:00   
75%              2023-07-22 22:00:00            0 days 00:15:00   
max              2023-07-31 22:00:00            0 days 01:40:00   
std                              NaN  0 days 00:10:32.716041213   

       trip_distance_kilometers  trip_distance_meters  start_stop_id  \
count                337.000000            337.000000     337.000000   
mean                   1.612916           1612.915857    1485.738872   
min                    0.106632            106.631517     684.000000   
25%                    0.632693            632.693044    1106.000000   
50%                    1.201332           1201.331651    1140.000000   
75%                    2.209057           2209.057367    1240.000000   
max                    5.892370           5892.369649    9702.000000   
std                    1.303314           1303.313921    1495.071249   

       end_stop_id  trip_duration_seconds  
count   337.000000             337.000000  
mean   1664.216617             880.415430  
min     683.000000             300.000000  
25%    1111.000000             600.000000  
50%    1172.000000             600.000000  
75%    1406.000000             900.000000  
max    9703.000000            6000.000000  
std    1848.382065             632.716041

In [264]:
# get statistics for the tier trips that start and end at a station
get_stats(evening_delay_tier_station_station, ['trip_duration_seconds', 'trip_distance_kilometers'])

column                                     trip_duration_seconds  \
rows                                                         337   
sum                                                     296700.0   
mean                                                   880.41543   
median                                                     600.0   
mode           0    600.0
Name: trip_duration_seconds, dtype:...   
max                                                       6000.0   
min                                                        300.0   
std_dev                                               632.716041   
variance                                           400329.588809   
skewness                                                3.843354   
kurtosis                                               23.646535   
percentile_25                                              600.0   
percentile_75                                              900.0   
iqr                                                        300.0   
range                                                     5700.0   
cv                                                      0.718656   
qd                                                           0.2   
cs                                                      0.006074   
ck                                                      0.037373   
cvs                                                     0.006074   
cvk                                                     0.037373   
cvcs                                                    0.006074   
cvck                                                    0.037373   
cvcv                                                    0.718656   
cvqd                                                         0.2   
cvr                                                     6.474216   
cvm                                                          1.0   
cvmed                                                   0.681496   
cvmode         0    0.681496
Name: trip_duration_seconds, dty...   

column                                  trip_distance_kilometers  
rows                                                         337  
sum                                                   543.552644  
mean                                                    1.612916  
median                                                  1.201332  
mode           0      0.106632
1      0.109852
2      0.11275...  
max                                                      5.89237  
min                                                     0.106632  
std_dev                                                 1.303314  
variance                                                1.698627  
skewness                                                1.203304  
kurtosis                                                0.927454  
percentile_25                                           0.632693  
percentile_75                                           2.209057  
iqr                                                     1.576364  
range                                                   5.785738  
cv                                                      0.808048  
qd                                                      0.554716  
cs                                                      0.923265  
ck                                                      0.711612  
cvs                                                     0.923265  
cvk                                                     0.711612  
cvcs                                                    0.923265  
cvck                                                    0.711612  
cvcv                                                    0.808048  
cvqd                                                    0.554716  
cvr                                                      3.58713  
cvm                                                          1.0  
cvmed                                                    0.74482  
cvmode         0

In [265]:
evening_delay_next = check_micromobility_datasets('next', evening_delay)

In [266]:
evening_delay_next.describe()

nextbike_trips_id      nextbike_trips_start_time  \
count       1.568000e+03                           1568   
mean        3.793780e+07  2023-07-16 12:25:58.737244672   
min         3.771653e+07            2023-07-01 20:01:00   
25%         3.782706e+07            2023-07-08 21:23:30   
50%         3.793750e+07            2023-07-15 20:41:00   
75%         3.804722e+07            2023-07-22 21:36:00   
max         3.817169e+07            2023-07-31 22:01:00   
std         1.285777e+05                            NaN   

             nextbike_trips_end_time              trip_duration  \
count                           1568                       1568   
mean   2023-07-16 12:41:46.454081792  0 days 00:15:47.716836734   
min              2023-07-01 20:11:00            0 days 00:05:00   
25%              2023-07-08 21:39:45            0 days 00:10:00   
50%              2023-07-15 20:48:30            0 days 00:15:00   
75%              2023-07-22 22:01:00            0 days 00:20:00   
max              2023-07-31 22:31:00            0 days 02:00:00   
std                              NaN  0 days 00:10:24.861963710   

       trip_distance_kilometers  trip_distance_meters  start_stop_id  \
count               1568.000000           1568.000000    1216.000000   
mean                   1.879000           1878.999607    1266.750000   
min                    0.100920            100.920160     161.000000   
25%                    0.856356            856.356069    1103.000000   
50%                    1.538932           1538.932316    1140.000000   
75%                    2.461684           2461.684104    1224.000000   
max                   13.022949          13022.949077    8950.000000   
std                    1.486588           1486.588465     959.090928   

       end_stop_id  trip_duration_seconds  
count   885.000000            1568.000000  
mean   1387.512994             947.716837  
min     161.000000             300.000000  
25%    1110.000000             600.000000  
50%    1153.000000             900.000000  
75%    1223.000000            1200.000000  
max    9780.000000            7200.000000  
std    1334.718523             624.861964

In [267]:
get_stats(evening_delay_next, ['trip_duration_seconds', 'trip_distance_kilometers'])

column                                     trip_duration_seconds  \
rows                                                        1568   
sum                                                    1486020.0   
mean                                                  947.716837   
median                                                     900.0   
mode           0    600.0
Name: trip_duration_seconds, dtype:...   
max                                                       7200.0   
min                                                        300.0   
std_dev                                               624.861964   
variance                                           390452.473692   
skewness                                                4.031047   
kurtosis                                               27.262882   
percentile_25                                              600.0   
percentile_75                                             1200.0   
iqr                                                        600.0   
range                                                     6900.0   
cv                                                      0.659334   
qd                                                      0.333333   
cs                                                      0.006451   
ck                                                       0.04363   
cvs                                                     0.006451   
cvk                                                      0.04363   
cvcs                                                    0.006451   
cvck                                                     0.04363   
cvcv                                                    0.659334   
cvqd                                                    0.333333   
cvr                                                     7.280656   
cvm                                                          1.0   
cvmed                                                   0.949651   
cvmode         0    0.6331
Name: trip_duration_seconds, dtype...   

column                                  trip_distance_kilometers  
rows                                                        1568  
sum                                                  2946.271384  
mean                                                       1.879  
median                                                  1.538932  
mode           0    0.110127
1    2.199943
Name: trip_distanc...  
max                                                    13.022949  
min                                                      0.10092  
std_dev                                                 1.486588  
variance                                                2.209945  
skewness                                                2.043639  
kurtosis                                                6.751446  
percentile_25                                           0.856356  
percentile_75                                           2.461684  
iqr                                                     1.605328  
range                                                  12.922029  
cv                                                       0.79116  
qd                                                      0.483818  
cs                                                      1.374717  
ck                                                       4.54157  
cvs                                                     1.374717  
cvk                                                      4.54157  
cvcs                                                    1.374717  
cvck                                                     4.54157  
cvcv                                                     0.79116  
cvqd                                                    0.483818  
cvr                                                     6.877079  
cvm                                                          1.0  
cvmed                                                   0.819017  
cvmode         0

In [268]:
# get entries where trips start and end at station
evening_delay_next_station_station = evening_delay_next[evening_delay_next['end_stop_id'].notna() & evening_delay_next['start_stop_id'].notna()]
evening_delay_next_station_station

nextbike_trips_id nextbike_trips_start_time nextbike_trips_end_time  \
1298316           37844432       2023-07-01 20:01:00     2023-07-01 20:21:00   
1421214           37998824       2023-07-01 20:01:00     2023-07-01 20:11:00   
1245075           37816421       2023-07-01 20:01:00     2023-07-01 20:11:00   
1218963           37716529       2023-07-01 20:16:00     2023-07-01 20:41:00   
1553014           38099832       2023-07-01 20:26:00     2023-07-01 20:41:00   
...                    ...                       ...                     ...   
1641137           37772556       2023-07-31 21:31:00     2023-07-31 21:46:00   
1332556           37860355       2023-07-31 21:31:00     2023-07-31 22:31:00   
1540818           38089733       2023-07-31 21:41:00     2023-07-31 21:46:00   
1223579           37720859       2023-07-31 21:46:00     2023-07-31 21:56:00   
1329312           37892654       2023-07-31 22:01:00     2023-07-31 22:16:00   

         nextbike_trips_start_at_station  nextbike_trips_end_at_station  \
1298316                            False                          False   
1421214                            False                           True   
1245075                            False                          False   
1218963                            False                          False   
1553014                            False                          False   
...                                  ...                            ...   
1641137                            False                          False   
1332556                            False                          False   
1540818                            False                           True   
1223579                            False                          False   
1329312                             True                          False   

        vehicle type   trip_duration  trip_distance_kilometers  \
1298316         bike 0 days 00:20:00                  2.689943   
1421214         bike 0 days 00:10:00                  0.580338   
1245075         bike 0 days 00:10:00                  3.114978   
1218963         bike 0 days 00:25:00                  2.825435   
1553014         bike 0 days 00:15:00                  0.929504   
...              ...             ...                       ...   
1641137         bike 0 days 00:15:00                  1.109057   
1332556         bike 0 days 01:00:00                  2.772292   
1540818         bike 0 days 00:05:00                  0.112330   
1223579         bike 0 days 00:10:00                  1.151484   
1329312         bike 0 days 00:15:00                  1.645817   

         trip_distance_meters  \
1298316           2689.943386   
1421214            580.338181   
1245075           3114.978233   
1218963           2825.434827   
1553014            929.503629   
...                       ...   
1641137           1109.057430   
1332556           2772.291604   
1540818            112.330142   
1223579           1151.483630   
1329312           1645.816542   

                                            start_location  \
1298316  b'\x01\x01\x00\x00\x00\x02\x10w\xf5*R\x1c@j\x1...   
1421214  b'\x01\x01\x00\x00\x00\xf3\x92\xff\xc9\xdf}\x1...   
1245075  b'\x01\x01\x00\x00\x00R\x0f\xd1\xe8\x0eb\x1c@\...   
1218963  b'\x01\x01\x00\x00\x00\xf6\xed$"\xfc[\x1c@\xfb...   
1553014  b'\x01\x01\x00\x00\x00\xf1\x9e\x03\xcb\x11b\x1...   
...                                                    ...   
1641137  b'\x01\x01\x00\x00\x00\x8e\x02D\xc1\x8cY\x1c@Q...   
1332556  b'\x01\x01\x00\x00\x00Z\x0f_&\x8a0\x1c@\x00\x8...   
1540818  b'\x01\x01\x00\x00\x00\xb5\x8bi\xa6{]\x1c@\xd7...   
1223579  b'\x01\x01\x00\x00\x00\xa7 ?\x1b\xb9~\x1c@\x9a...   
1329312  b'\x01\x01\x00\x00\x00|H\xf8\xde\xdf`\x1c@/\xe...   

                                              end_location  start_stop_id  \
1298316  b'\x01\x01\x00\x00\x00\x7f\x16K\x91|e\x1c@\x88...         1231.0   
1421214  b'\x01\x01\x00\x00\x00/1\x96\xe9\x97x\x1c@\x86...

In [269]:
evening_delay_next_station_station.describe()

nextbike_trips_id      nextbike_trips_start_time  \
count       7.390000e+02                            739   
mean        3.793823e+07  2023-07-15 18:51:41.001352960   
min         3.771653e+07            2023-07-01 20:01:00   
25%         3.782730e+07            2023-07-08 20:36:00   
50%         3.793560e+07            2023-07-14 21:01:00   
75%         3.804554e+07            2023-07-21 21:06:00   
max         3.817169e+07            2023-07-31 22:01:00   
std         1.283279e+05                            NaN   

             nextbike_trips_end_time              trip_duration  \
count                            739                        739   
mean   2023-07-15 19:05:53.098782208  0 days 00:14:12.097428958   
min              2023-07-01 20:11:00            0 days 00:05:00   
25%              2023-07-08 20:51:00            0 days 00:10:00   
50%              2023-07-14 21:16:00            0 days 00:10:00   
75%              2023-07-21 21:16:00            0 days 00:15:00   
max              2023-07-31 22:31:00            0 days 02:00:00   
std                              NaN  0 days 00:09:32.665816018   

       trip_distance_kilometers  trip_distance_meters  start_stop_id  \
count                739.000000            739.000000     739.000000   
mean                   1.529174           1529.174352    1331.815968   
min                    0.100920            100.920160     161.000000   
25%                    0.739921            739.921483    1103.000000   
50%                    1.241755           1241.754916    1140.000000   
75%                    1.968413           1968.413009    1223.000000   
max                    9.640671           9640.671235    8507.000000   
std                    1.195923           1195.923221    1106.684830   

       end_stop_id  trip_duration_seconds  
count   739.000000             739.000000  
mean   1423.359946             852.097429  
min     161.000000             300.000000  
25%    1112.000000             600.000000  
50%    1160.000000             600.000000  
75%    1223.000000             900.000000  
max    9780.000000            7200.000000  
std    1406.463053             572.665816

In [270]:
# get statistics for the tier trips that start and end at a station
get_stats(evening_delay_next_station_station, ['trip_duration_seconds', 'trip_distance_kilometers'])

column                                     trip_duration_seconds  \
rows                                                         739   
sum                                                     629700.0   
mean                                                  852.097429   
median                                                     600.0   
mode           0    600.0
Name: trip_duration_seconds, dtype:...   
max                                                       7200.0   
min                                                        300.0   
std_dev                                               572.665816   
variance                                           327946.136836   
skewness                                                5.105904   
kurtosis                                               44.312995   
percentile_25                                              600.0   
percentile_75                                              900.0   
iqr                                                        300.0   
range                                                     6900.0   
cv                                                      0.672066   
qd                                                           0.2   
cs                                                      0.008916   
ck                                                       0.07738   
cvs                                                     0.008916   
cvk                                                      0.07738   
cvcs                                                    0.008916   
cvck                                                     0.07738   
cvcv                                                    0.672066   
cvqd                                                         0.2   
cvr                                                     8.097666   
cvm                                                          1.0   
cvmed                                                   0.704145   
cvmode         0    0.704145
Name: trip_duration_seconds, dty...   

column                                  trip_distance_kilometers  
rows                                                         739  
sum                                                  1130.059846  
mean                                                    1.529174  
median                                                  1.241755  
mode           0    0.110127
Name: trip_distance_kilometers, ...  
max                                                     9.640671  
min                                                      0.10092  
std_dev                                                 1.195923  
variance                                                1.430232  
skewness                                                2.002379  
kurtosis                                                6.553317  
percentile_25                                           0.739921  
percentile_75                                           1.968413  
iqr                                                     1.228492  
range                                                   9.539751  
cv                                                      0.782071  
qd                                                      0.453597  
cs                                                      1.674337  
ck                                                      5.479714  
cvs                                                     1.674337  
cvk                                                     5.479714  
cvcs                                                    1.674337  
cvck                                                    5.479714  
cvcv                                                    0.782071  
cvqd                                                    0.453597  
cvr                                                     6.238498  
cvm                                                          1.0  
cvmed                                                   0.812043  
cvmode         0

In [271]:
evening_no_delay = no_delay[(no_delay['scheduled_arrival_time'].dt.hour > 19) & (no_delay['scheduled_arrival_time'].dt.hour < 22)]
evening_no_delay

route_id  agency_id route_short_name  route_type route_type_name  \
70824         608          6              608           3             Bus   
70826         537          8              537           3             Bus   
70827         845         12              845           3             Bus   
70828         610          6              610           3             Bus   
70833         610          6              610           3             Bus   
...           ...        ...              ...         ...             ...   
2557442       610          6              610           3             Bus   
2557445       606          6              606           3             Bus   
2557446       611          6              611           3             Bus   
2557454        66          6               66           0            Tram   
2557458       601          6              601           3             Bus   

                                         agency_name  service_id  \
70824              SWB Stadtwerke Bonn Verkehrs GmbH         130   
70826       RSVG Rhein-Sieg-Verkehrsgesellschaft mbH         133   
70827    RVK Regionalverkehr Köln GmbH NL Meckenheim         130   
70828              SWB Stadtwerke Bonn Verkehrs GmbH         130   
70833              SWB Stadtwerke Bonn Verkehrs GmbH         130   
...                                              ...         ...   
2557442            SWB Stadtwerke Bonn Verkehrs GmbH          43   
2557445            SWB Stadtwerke Bonn Verkehrs GmbH          43   
2557446            SWB Stadtwerke Bonn Verkehrs GmbH           3   
2557454            SWB Stadtwerke Bonn Verkehrs GmbH       27311   
2557458            SWB Stadtwerke Bonn Verkehrs GmbH          43   

                                                   trip_id  \
70824    6080202-608-006-1574.2.24:192900-47-1_DA646D28...   
70826    52-537-008-2140.2.21:193200-36-1_5CBE0BEB-982B...   
70827    1650-845-012-1842.2.22:192000-29-1_72CFAE2A-15...   
70828    6100200-610-006-1341.2.24:191300-53-1_1AAF8176...   
70833    6100195-610-006-1756.2.21:191900-54-1_3E71FA36...   
...                                                    ...   
2557442  6100026-610-006-1341.2.24:215100-53-1_B2803993...   
2557445  6060040-606-006-1584.2.22:211000-44-1_CD3EBE21...   
2557446  6110045-611-006-1723.2.21:215000-60-1_CEA94F99...   
2557454  660293-66-006-1584.1.11:214100-25-1_A788DE18-7...   
2557458  6010023-601-006-1293.2.21:214200-46-1_33985831...   

                trip_headsign  direction_id  ...  delay_span  \
70824      Hardthöhe/Südwache             1  ...           0   
70826                Bonn Hbf             0  ...           0   
70827                Bonn Hbf             1  ...           0   
70828            Giselherstr.             1  ...         0-5   
70833             Duisdorf Bf             0  ...           0   
...                       ...           ...  ...         ...   
2557442          Giselherstr.             1  ...           0   
2557445    Hardtberg Klinikum             1  ...           0   
2557446  Lessenich Sportplatz             0  ...           0   
2557454           Siegburg Bf             0  ...           0   
2557458    Agnetendorfer Str.             0  ...           0   

         arrival_delay_span weather_int time_span_arrival  \
70824                     0           0      evening rush   
70826                     0           0           evening   
70827                     0           0                 0   
70828                     0           0           evening   
70833                     0           0      evening rush   
...                     ...         ...               ...   
2557442                   0           1           evening   
2557445                   0           1           evening   
2557446                   0           1           evening   
2557454                   0           1           evening   
2557458                   0           1           evening   

         time_span_i

In [272]:
get_stats(evening_no_delay, ['tier_trips_count', 'tier_trips_end_at_station_count', 'nextbike_trips_count', 'nextbike_trips_end_at_station_count', 'current_temp', 'current_precipitation_volume'])

/tmp/ipykernel_2575952/41814695.py:51: RuntimeWarning: invalid value encountered in scalar divide
  qd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:55: RuntimeWarning: invalid value encountered in scalar divide
  cvqd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:51: RuntimeWarning: invalid value encountered in scalar divide
  qd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:55: RuntimeWarning: invalid value encountered in scalar divide
  cvqd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:51: RuntimeWarning: invalid value encountered in scalar divide
  qd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:55: RuntimeWarning: invalid value encountered in scalar divide
  cvqd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:51: RuntimeWarning: invalid value encountered in scalar divide
  qd = iqr / (percentile_75 + percenti

column                                        tier_trips_count  \
rows                                                     54395   
sum                                                       1668   
mean                                                  0.030665   
median                                                     0.0   
mode               0    0
Name: tier_trips_count, dtype: int64   
max                                                          5   
min                                                          0   
std_dev                                               0.195589   
variance                                              0.038255   
skewness                                               7.48692   
kurtosis                                             69.297148   
percentile_25                                              0.0   
percentile_75                                              0.0   
iqr                                                        0.0   
range                                                        5   
cv                                                    6.378345   
qd                                                         NaN   
cs                                                   38.278785   
ck                                                  354.299321   
cvs                                                  38.278785   
cvk                                                 354.299321   
cvcs                                                 38.278785   
cvck                                                354.299321   
cvcv                                                  6.378345   
cvqd                                                       NaN   
cvr                                                 163.054556   
cvm                                                        1.0   
cvmed                                                      0.0   
cvmode         0    0.0
Name: tier_trips_count, dtype: float64   

column                           tier_trips_end_at_station_count  \
rows                                                       54395   
sum                                                         1363   
mean                                                    0.025057   
median                                                       0.0   
mode           0    0
Name: tier_trips_end_at_station_count, ...   
max                                                            5   
min                                                            0   
std_dev                                                 0.174739   
variance                                                0.030534   
skewness                                                8.150465   
kurtosis                                               82.899734   
percentile_25                                                0.0   
percentile_75                                                0.0   
iqr                                                          0.0   
range                                                          5   
cv                                                      6.973526   
qd                                                           NaN   
cs                                                      46.64371   
ck                                                    474.420955   
cvs                                                     46.64371   
cvk                                                   474.420955   
cvcs                                                    46.64371   
cvck                                                  474.420955   
cvcv                                                    6.973526   
cvqd                                                         NaN   
cvr                                                   199.541453   
cvm                                                          1.0   
cvmed                                                        0.0   
cvmode         0    0.0
Name: tier_trips_end_at

In [273]:
evening_no_delay_tier = check_micromobility_datasets('tier', evening_no_delay)

In [274]:
evening_no_delay_tier.describe()

tier_trips_id       tier_trips_start_time  \
count   6.720000e+02                         672   
mean    8.002994e+08  2023-07-15 23:03:12.500000   
min     7.822648e+08         2023-07-01 20:05:00   
25%     7.823791e+08         2023-07-08 20:05:00   
50%     8.086409e+08         2023-07-14 20:52:30   
75%     8.087662e+08         2023-07-22 21:16:15   
max     8.323067e+08         2023-07-31 21:55:00   
std     1.751198e+07                         NaN   

                 tier_trips_end_time              trip_duration  \
count                            672                        672   
mean   2023-07-15 23:18:01.785714176  0 days 00:14:49.285714285   
min              2023-07-01 20:15:00            0 days 00:05:00   
25%              2023-07-08 20:18:45            0 days 00:10:00   
50%              2023-07-14 21:15:00            0 days 00:10:00   
75%              2023-07-22 21:31:15            0 days 00:15:00   
max              2023-07-31 22:00:00            0 days 01:55:00   
std                              NaN  0 days 00:11:10.922643792   

       trip_distance_kilometers  trip_distance_meters  start_stop_id  \
count                672.000000            672.000000     535.000000   
mean                   1.909021           1909.021069    1043.259813   
min                    0.101595            101.594715     161.000000   
25%                    0.830290            830.289772     687.000000   
50%                    1.422016           1422.015883    1103.000000   
75%                    2.508883           2508.882840    1182.500000   
max                    8.887499           8887.498628    9029.000000   
std                    1.555337           1555.336757     630.281996   

       end_stop_id  trip_duration_seconds  
count   346.000000             672.000000  
mean   1357.710983             889.285714  
min     161.000000             300.000000  
25%    1104.000000             600.000000  
50%    1150.000000             600.000000  
75%    1240.750000             900.000000  
max    9703.000000            6900.000000  
std    1312.884258             670.922644

In [275]:
get_stats(evening_no_delay_tier, ['trip_duration_seconds', 'trip_distance_kilometers'])

column                                     trip_duration_seconds  \
rows                                                         672   
sum                                                     597600.0   
mean                                                  889.285714   
median                                                     600.0   
mode           0    600.0
Name: trip_duration_seconds, dtype:...   
max                                                       6900.0   
min                                                        300.0   
std_dev                                               670.922644   
variance                                           450137.193954   
skewness                                                4.780895   
kurtosis                                               32.079581   
percentile_25                                              600.0   
percentile_75                                              900.0   
iqr                                                        300.0   
range                                                     6600.0   
cv                                                      0.754451   
qd                                                           0.2   
cs                                                      0.007126   
ck                                                      0.047814   
cvs                                                     0.007126   
cvk                                                     0.047814   
cvcs                                                    0.007126   
cvck                                                    0.047814   
cvcv                                                    0.754451   
cvqd                                                         0.2   
cvr                                                     7.421687   
cvm                                                          1.0   
cvmed                                                   0.674699   
cvmode         0    0.674699
Name: trip_duration_seconds, dty...   

column                                  trip_distance_kilometers  
rows                                                         672  
sum                                                  1282.862158  
mean                                                    1.909021  
median                                                  1.422016  
mode           0      0.101595
1      0.103876
2      0.10487...  
max                                                     8.887499  
min                                                     0.101595  
std_dev                                                 1.555337  
variance                                                2.419072  
skewness                                                1.491662  
kurtosis                                                2.295419  
percentile_25                                            0.83029  
percentile_75                                           2.508883  
iqr                                                     1.678593  
range                                                   8.785904  
cv                                                       0.81473  
qd                                                      0.502697  
cs                                                      0.959061  
ck                                                      1.475834  
cvs                                                     0.959061  
cvk                                                     1.475834  
cvcs                                                    0.959061  
cvck                                                    1.475834  
cvcv                                                     0.81473  
cvqd                                                    0.502697  
cvr                                                     4.602309  
cvm                                                          1.0  
cvmed                                                   0.744893  
cvmode         0

In [276]:
# get entries where trips start and end at station
evening_no_delay_tier_station_station = evening_no_delay_tier[evening_no_delay_tier['end_stop_id'].notna() & evening_no_delay_tier['start_stop_id'].notna()]
evening_no_delay_tier_station_station

tier_trips_id tier_trips_start_time tier_trips_end_time vehicle type  \
3258480      782435847   2023-07-01 20:05:00 2023-07-01 20:15:00    e-scooter   
3048678      782308675   2023-07-01 20:20:00 2023-07-01 20:30:00    e-scooter   
2907344      782265307   2023-07-01 20:20:00 2023-07-01 20:30:00    e-scooter   
3171427      782355812   2023-07-01 20:20:00 2023-07-01 20:30:00    e-scooter   
2937706      782274429   2023-07-01 20:20:00 2023-07-01 20:40:00    e-scooter   
...                ...                   ...                 ...          ...   
3299964      832107425   2023-07-31 20:50:00 2023-07-31 21:00:00    e-scooter   
3412614      832195764   2023-07-31 20:50:00 2023-07-31 21:05:00    e-scooter   
3461090      832242303   2023-07-31 20:55:00 2023-07-31 21:00:00    e-scooter   
3385595      832169884   2023-07-31 21:00:00 2023-07-31 21:10:00    e-scooter   
3416889      832199855   2023-07-31 21:10:00 2023-07-31 21:15:00    e-scooter   

          trip_duration  trip_distance_kilometers  trip_distance_meters  \
3258480 0 days 00:10:00                  1.683868           1683.868403   
3048678 0 days 00:10:00                  0.366805            366.804928   
2907344 0 days 00:10:00                  0.507613            507.613257   
3171427 0 days 00:10:00                  0.129378            129.377557   
2937706 0 days 00:20:00                  0.287945            287.944581   
...                 ...                       ...                   ...   
3299964 0 days 00:10:00                  1.325877           1325.876813   
3412614 0 days 00:15:00                  2.405022           2405.021608   
3461090 0 days 00:05:00                  0.512001            512.001489   
3385595 0 days 00:10:00                  0.287767            287.767278   
3416889 0 days 00:05:00                  0.960512            960.511916   

         start_stop_id                            start_stop_name  \
3258480         1221.0                          Bonn Kaufmannstr.   
3048678          687.0                                   Bonn Hbf   
2907344         1223.0                            Bonn Beringstr.   
3171427          694.0                     Bonn Tannenbusch Mitte   
2937706         1385.0                          Bonn Merler Allee   
...                ...                                        ...   
3299964          687.0                                   Bonn Hbf   
3412614          687.0                                   Bonn Hbf   
3461090          687.0                                   Bonn Hbf   
3385595         1115.0  Bonn Bertha-Von-Suttner-Pl./Beethovenhaus   
3416889         1500.0                 Bonn Konrad-Adenauer-Platz   

                                         start_buffer_zone  end_stop_id  \
3258480  801621     POLYGON ((7.157885983913106 50.7227...       1190.0   
3048678  801621     POLYGON ((7.157885983913106 50.7227...       1106.0   
2907344  801621     POLYGON ((7.157885983913106 50.7227...        687.0   
3171427  801621     POLYGON ((7.157885983913106 50.7227...        694.0   
2937706  801621     POLYGON ((7.157885983913106 50.7227...       1386.0   
...                                                    ...          ...   
3299964  801621     POLYGON ((7.157885983913106 50.7227...       1240.0   
3412614  801621     POLYGON ((7.157885983913106 50.7227...       1235.0   
3461090  801621     POLYGON ((7.157885983913106 50.7227...       1146.0   
3385595  801621     POLYGON ((7.157885983913106 50.7227...       1111.0   
3416889  801621     POLYGON ((7.157885983913106 50.7227...       1504.0   

                       end_stop_name  \
3258480               Bonn Zeisigweg   
3048678        Bonn Thomas-Mann-Str.   
2907344                     Bonn Hbf   
3171427       Bonn Tannenbusch Mitte   
2937706        Bonn Röttgen Schleife   
...                              ...   
3299964     Bonn Poppelsdorfer Platz   
3412614              Bonn Konradstr.   
3461090                Bonn Bachstr.   
33855

In [277]:
evening_no_delay_tier_station_station.describe()

tier_trips_id          tier_trips_start_time  \
count   3.060000e+02                            306   
mean    8.019132e+08  2023-07-16 13:12:23.137254656   
min     7.822653e+08            2023-07-01 20:05:00   
25%     7.823843e+08            2023-07-08 20:06:15   
50%     8.086602e+08            2023-07-15 20:20:00   
75%     8.087823e+08            2023-07-24 14:33:45   
max     8.323066e+08            2023-07-31 21:10:00   
std     1.761313e+07                            NaN   

                 tier_trips_end_time              trip_duration  \
count                            306                        306   
mean   2023-07-16 13:26:00.784313600  0 days 00:13:37.647058823   
min              2023-07-01 20:15:00            0 days 00:05:00   
25%              2023-07-08 20:17:30            0 days 00:10:00   
50%              2023-07-15 20:37:30            0 days 00:10:00   
75%              2023-07-24 14:58:45            0 days 00:15:00   
max              2023-07-31 21:15:00            0 days 01:40:00   
std                              NaN  0 days 00:09:23.725040179   

       trip_distance_kilometers  trip_distance_meters  start_stop_id  \
count                306.000000            306.000000     306.000000   
mean                   1.582313           1582.312694    1063.330065   
min                    0.101595            101.594715     371.000000   
25%                    0.615495            615.494735     687.000000   
50%                    1.129550           1129.549789    1104.000000   
75%                    2.151007           2151.007437    1169.500000   
max                    8.887499           8887.498628    9029.000000   
std                    1.344074           1344.073933     605.055878   

       end_stop_id  trip_duration_seconds  
count   306.000000             306.000000  
mean   1378.611111             817.647059  
min     683.000000             300.000000  
25%    1106.000000             600.000000  
50%    1151.000000             600.000000  
75%    1240.750000             900.000000  
max    9703.000000            6000.000000  
std    1296.594170             563.725040

In [278]:
# get statistics for the tier trips that start and end at a station
get_stats(evening_no_delay_tier_station_station, ['trip_duration_seconds', 'trip_distance_kilometers'])

column                                     trip_duration_seconds  \
rows                                                         306   
sum                                                     250200.0   
mean                                                  817.647059   
median                                                     600.0   
mode           0    600.0
Name: trip_duration_seconds, dtype:...   
max                                                       6000.0   
min                                                        300.0   
std_dev                                                563.72504   
variance                                           317785.920926   
skewness                                                4.407613   
kurtosis                                               30.704866   
percentile_25                                              600.0   
percentile_75                                              900.0   
iqr                                                        300.0   
range                                                     5700.0   
cv                                                      0.689448   
qd                                                           0.2   
cs                                                      0.007819   
ck                                                      0.054468   
cvs                                                     0.007819   
cvk                                                     0.054468   
cvcs                                                    0.007819   
cvck                                                    0.054468   
cvcv                                                    0.689448   
cvqd                                                         0.2   
cvr                                                     6.971223   
cvm                                                          1.0   
cvmed                                                   0.733813   
cvmode         0    0.733813
Name: trip_duration_seconds, dty...   

column                                  trip_distance_kilometers  
rows                                                         306  
sum                                                   484.187684  
mean                                                    1.582313  
median                                                   1.12955  
mode           0      0.101595
1      0.103876
2      0.10644...  
max                                                     8.887499  
min                                                     0.101595  
std_dev                                                 1.344074  
variance                                                1.806535  
skewness                                                1.673119  
kurtosis                                                3.746909  
percentile_25                                           0.615495  
percentile_75                                           2.151007  
iqr                                                     1.535513  
range                                                   8.785904  
cv                                                      0.849436  
qd                                                      0.555038  
cs                                                      1.244811  
ck                                                      2.787726  
cvs                                                     1.244811  
cvk                                                     2.787726  
cvcs                                                    1.244811  
cvck                                                    2.787726  
cvcv                                                    0.849436  
cvqd                                                    0.555038  
cvr                                                     5.552571  
cvm                                                          1.0  
cvmed                                                    0.71386  
cvmode         0

In [279]:
evening_no_delay_next = check_micromobility_datasets('next', evening_no_delay)

In [280]:
evening_no_delay_next.describe()

nextbike_trips_id      nextbike_trips_start_time  \
count       1.305000e+03                           1305   
mean        3.794256e+07  2023-07-16 05:42:43.172413696   
min         3.771653e+07            2023-07-01 20:11:00   
25%         3.783094e+07            2023-07-08 20:16:00   
50%         3.794729e+07            2023-07-15 20:16:00   
75%         3.805036e+07            2023-07-22 20:51:00   
max         3.817077e+07            2023-07-31 21:56:00   
std         1.282935e+05                            NaN   

             nextbike_trips_end_time              trip_duration  \
count                           1305                       1305   
mean   2023-07-16 05:58:03.356321792  0 days 00:15:20.183908045   
min              2023-07-01 20:21:00            0 days 00:05:00   
25%              2023-07-08 20:26:00            0 days 00:10:00   
50%              2023-07-15 20:31:00            0 days 00:15:00   
75%              2023-07-22 21:11:00            0 days 00:20:00   
max              2023-07-31 22:06:00            0 days 01:30:00   
std                              NaN  0 days 00:08:21.944650743   

       trip_distance_kilometers  trip_distance_meters  start_stop_id  \
count               1305.000000           1305.000000    1090.000000   
mean                   1.884745           1884.745043    1071.053211   
min                    0.100920            100.920160     161.000000   
25%                    0.939460            939.459929     687.000000   
50%                    1.511361           1511.360928    1103.000000   
75%                    2.387797           2387.797312    1160.000000   
max                   13.022949          13022.949077    9780.000000   
std                    1.470614           1470.613797     863.457136   

       end_stop_id  trip_duration_seconds  
count   732.000000            1305.000000  
mean   1310.622951             920.183908  
min     161.000000             300.000000  
25%    1113.750000             600.000000  
50%    1160.000000             900.000000  
75%    1223.000000            1200.000000  
max    9702.000000            5400.000000  
std    1090.739184             501.944651

In [281]:
get_stats(evening_no_delay_next, ['trip_duration_seconds', 'trip_distance_kilometers'])

column                                     trip_duration_seconds  \
rows                                                        1305   
sum                                                    1200840.0   
mean                                                  920.183908   
median                                                     900.0   
mode           0    600.0
Name: trip_duration_seconds, dtype:...   
max                                                       5400.0   
min                                                        300.0   
std_dev                                               501.944651   
variance                                            251948.43241   
skewness                                                2.912494   
kurtosis                                               17.262957   
percentile_25                                              600.0   
percentile_75                                             1200.0   
iqr                                                        600.0   
range                                                     5100.0   
cv                                                      0.545483   
qd                                                      0.333333   
cs                                                      0.005802   
ck                                                      0.034392   
cvs                                                     0.005802   
cvk                                                     0.034392   
cvcs                                                    0.005802   
cvck                                                    0.034392   
cvcv                                                    0.545483   
cvqd                                                    0.333333   
cvr                                                      5.54237   
cvm                                                          1.0   
cvmed                                                   0.978065   
cvmode         0    0.652044
Name: trip_duration_seconds, dty...   

column                                  trip_distance_kilometers  
rows                                                        1305  
sum                                                  2459.592281  
mean                                                    1.884745  
median                                                  1.511361  
mode           0    0.98257
Name: trip_distance_kilometers, d...  
max                                                    13.022949  
min                                                      0.10092  
std_dev                                                 1.470614  
variance                                                2.162705  
skewness                                                2.151608  
kurtosis                                                6.840153  
percentile_25                                            0.93946  
percentile_75                                           2.387797  
iqr                                                     1.448337  
range                                                  12.922029  
cv                                                      0.780272  
qd                                                      0.435295  
cs                                                      1.463068  
ck                                                      4.651223  
cvs                                                     1.463068  
cvk                                                     4.651223  
cvcs                                                    1.463068  
cvck                                                    4.651223  
cvcv                                                    0.780272  
cvqd                                                    0.435295  
cvr                                                     6.856115  
cvm                                                          1.0  
cvmed                                                   0.801891  
cvmode         0

In [282]:
# get entries where trips start and end at station
evening_no_delay_next_station_station = evening_no_delay_next[evening_no_delay_next['end_stop_id'].notna() & evening_no_delay_next['start_stop_id'].notna()]
evening_no_delay_next_station_station

nextbike_trips_id nextbike_trips_start_time nextbike_trips_end_time  \
1218963           37716529       2023-07-01 20:16:00     2023-07-01 20:41:00   
1649771           37781190       2023-07-01 20:21:00     2023-07-01 20:31:00   
1361050           37933936       2023-07-01 20:26:00     2023-07-01 20:36:00   
1588995           38130455       2023-07-01 20:36:00     2023-07-01 20:51:00   
1436917           38008727       2023-07-01 20:41:00     2023-07-01 21:16:00   
...                    ...                       ...                     ...   
1469167           38033725       2023-07-31 21:26:00     2023-07-31 21:36:00   
1540817           38089732       2023-07-31 21:26:00     2023-07-31 21:41:00   
1392716           37984594       2023-07-31 21:31:00     2023-07-31 21:46:00   
1258227           37738223       2023-07-31 21:31:00     2023-07-31 21:41:00   
1670611           37802030       2023-07-31 21:56:00     2023-07-31 22:06:00   

         nextbike_trips_start_at_station  nextbike_trips_end_at_station  \
1218963                            False                          False   
1649771                            False                          False   
1361050                             True                          False   
1588995                            False                          False   
1436917                            False                          False   
...                                  ...                            ...   
1469167                            False                          False   
1540817                            False                          False   
1392716                            False                          False   
1258227                            False                          False   
1670611                            False                          False   

        vehicle type   trip_duration  trip_distance_kilometers  \
1218963         bike 0 days 00:25:00                  2.825435   
1649771         bike 0 days 00:10:00                  0.574793   
1361050         bike 0 days 00:10:00                  0.784946   
1588995         bike 0 days 00:15:00                  1.988363   
1436917         bike 0 days 00:35:00                  6.703541   
...              ...             ...                       ...   
1469167         bike 0 days 00:10:00                  0.939808   
1540817         bike 0 days 00:15:00                  1.422846   
1392716         bike 0 days 00:15:00                  2.389327   
1258227         bike 0 days 00:10:00                  1.822654   
1670611         bike 0 days 00:10:00                  1.127301   

         trip_distance_meters  \
1218963           2825.434827   
1649771            574.792584   
1361050            784.946180   
1588995           1988.362862   
1436917           6703.540950   
...                       ...   
1469167            939.808209   
1540817           1422.846299   
1392716           2389.326515   
1258227           1822.654198   
1670611           1127.301066   

                                            start_location  \
1218963  b'\x01\x01\x00\x00\x00\xf6\xed$"\xfc[\x1c@\xfb...   
1649771  b'\x01\x01\x00\x00\x00\x18\xd2\xe1!\x8c_\x1c@J...   
1361050  b'\x01\x01\x00\x00\x00\xf4\x8a\xa7\x1ei`\x1c@c...   
1588995  b'\x01\x01\x00\x00\x00\x9d\xd7\xd8%\xaag\x1c@\...   
1436917  b'\x01\x01\x00\x00\x00\xc5:U\xbegd\x1c@\x8b\xf...   
...                                                    ...   
1469167  b'\x01\x01\x00\x00\x00|\xb9O\x8e\x02d\x1c@\xf6...   
1540817  b'\x01\x01\x00\x00\x00\x04\xacU\xbb&d\x1c@\xaf...   
1392716  b'\x01\x01\x00\x00\x00\xac\xc9SV\xd3e\x1c@+MJA...   
1258227  b'\x01\x01\x00\x00\x00\x17\x9c\xc1\xdf/V\x1c@\...   
1670611  b'\x01\x01\x00\x00\x00\xe7\xfc\x14\xc7\x81g\x1...   

                                              end_location  start_stop_id  \
1218963  b'\x01\x01\x00\x00\x00\xddC\xc2\xf7\xfef\x1c@\...         1182.0   
1649771  b'\x01\x01\x00\x00\x00\xaf@\xf4\xa4LZ\x1c@\xbc...

In [283]:
evening_no_delay_next_station_station.describe()

nextbike_trips_id      nextbike_trips_start_time  \
count       6.430000e+02                            643   
mean        3.794369e+07  2023-07-15 16:32:30.699844352   
min         3.771653e+07            2023-07-01 20:16:00   
25%         3.782470e+07            2023-07-07 21:23:30   
50%         3.795065e+07            2023-07-14 20:21:00   
75%         3.805476e+07            2023-07-21 21:23:30   
max         3.817077e+07            2023-07-31 21:56:00   
std         1.324728e+05                            NaN   

             nextbike_trips_end_time              trip_duration  \
count                            643                        643   
mean   2023-07-15 16:46:19.595645440  0 days 00:13:48.895800933   
min              2023-07-01 20:31:00            0 days 00:05:00   
25%              2023-07-07 21:38:30            0 days 00:10:00   
50%              2023-07-14 20:41:00            0 days 00:15:00   
75%              2023-07-21 21:36:00            0 days 00:15:00   
max              2023-07-31 22:06:00            0 days 01:00:00   
std                              NaN  0 days 00:06:44.306097641   

       trip_distance_kilometers  trip_distance_meters  start_stop_id  \
count                643.000000            643.000000     643.000000   
mean                   1.541099           1541.099334    1114.262830   
min                    0.100920            100.920160     161.000000   
25%                    0.825008            825.007810     687.000000   
50%                    1.247518           1247.517568    1106.000000   
75%                    1.929398           1929.398245    1161.000000   
max                    9.640671           9640.671235    9780.000000   
std                    1.141667           1141.666591     890.969753   

       end_stop_id  trip_duration_seconds  
count   643.000000             643.000000  
mean   1336.051322             828.895801  
min     161.000000             300.000000  
25%    1115.000000             600.000000  
50%    1160.000000             900.000000  
75%    1223.000000             900.000000  
max    9702.000000            3600.000000  
std    1150.280986             404.306098

In [284]:
# get statistics for the tier trips that start and end at a station
get_stats(evening_no_delay_next_station_station, ['trip_duration_seconds', 'trip_distance_kilometers'])

column                                     trip_duration_seconds  \
rows                                                         643   
sum                                                     532980.0   
mean                                                  828.895801   
median                                                     900.0   
mode           0    600.0
Name: trip_duration_seconds, dtype:...   
max                                                       3600.0   
min                                                        300.0   
std_dev                                               404.306098   
variance                                            163463.42059   
skewness                                                2.161158   
kurtosis                                                9.721423   
percentile_25                                              600.0   
percentile_75                                              900.0   
iqr                                                        300.0   
range                                                     3300.0   
cv                                                      0.487765   
qd                                                           0.2   
cs                                                      0.005345   
ck                                                      0.024045   
cvs                                                     0.005345   
cvk                                                     0.024045   
cvcs                                                    0.005345   
cvck                                                    0.024045   
cvcv                                                    0.487765   
cvqd                                                         0.2   
cvr                                                       3.9812   
cvm                                                          1.0   
cvmed                                                   1.085782   
cvmode         0    0.723855
Name: trip_duration_seconds, dty...   

column                                  trip_distance_kilometers  
rows                                                         643  
sum                                                   990.926872  
mean                                                    1.541099  
median                                                  1.247518  
mode           0    0.98257
Name: trip_distance_kilometers, d...  
max                                                     9.640671  
min                                                      0.10092  
std_dev                                                 1.141667  
variance                                                1.303403  
skewness                                                2.210288  
kurtosis                                                8.186553  
percentile_25                                           0.825008  
percentile_75                                           1.929398  
iqr                                                      1.10439  
range                                                   9.539751  
cv                                                      0.740813  
qd                                                      0.400954  
cs                                                      1.936019  
ck                                                      7.170704  
cvs                                                     1.936019  
cvk                                                     7.170704  
cvcs                                                    1.936019  
cvck                                                    7.170704  
cvcv                                                    0.740813  
cvqd                                                    0.400954  
cvr                                                     6.190225  
cvm                                                          1.0  
cvmed                                                   0.809498  
cvmode         0

In [285]:
evening_nan_delay = nan_delay[(nan_delay['scheduled_arrival_time'].dt.hour > 19) & (nan_delay['scheduled_arrival_time'].dt.hour < 22)]
evening_nan_delay

route_id  agency_id route_short_name  route_type route_type_name  \
70819         610          6              610           3             Bus   
70829         601          6              601           3             Bus   
70831         633          6              633           3             Bus   
70837          65          6               65           0            Tram   
70838         632          6              632           3             Bus   
...           ...        ...              ...         ...             ...   
2557459        65          6               65           0            Tram   
2557461       537          8              537           3             Bus   
2557463        65          6               65           0            Tram   
2557465       601          6              601           3             Bus   
2557466       604          6              604           3             Bus   

                                      agency_name  service_id  \
70819           SWB Stadtwerke Bonn Verkehrs GmbH         130   
70829           SWB Stadtwerke Bonn Verkehrs GmbH         130   
70831           SWB Stadtwerke Bonn Verkehrs GmbH         130   
70837           SWB Stadtwerke Bonn Verkehrs GmbH       26814   
70838           SWB Stadtwerke Bonn Verkehrs GmbH         130   
...                                           ...         ...   
2557459         SWB Stadtwerke Bonn Verkehrs GmbH       26825   
2557461  RSVG Rhein-Sieg-Verkehrsgesellschaft mbH          64   
2557463         SWB Stadtwerke Bonn Verkehrs GmbH       26826   
2557465         SWB Stadtwerke Bonn Verkehrs GmbH          43   
2557466         SWB Stadtwerke Bonn Verkehrs GmbH          43   

                                                   trip_id  \
70819    6100193-610-006-1756.2.21:185900-54-1_2E90695B...   
70829    6010263-601-006-1293.2.21:194100-46-1_C3543AF6...   
70831    6330118-633-006-1584.2.24:194900-24-1_7B1A46C5...   
70837    650778-65-006-1406.1.12:193400-24-178_1F2C20F0...   
70838    6320229-632-006-1293.2.21:193800-23-1_61D7079A...   
...                                                    ...   
2557459  651172-65-006-1406.1.12:215300-24-179_A4DB4CF1...   
2557461  120-537-008-687.2.36:213900-37-1_D2EB4101-0EA3...   
2557463  651147-65-006-1593.1.12:213500-24-179_E84B2896...   
2557465  6010030-601-006-9478.2.22:214200-44-1_E7505DAB...   
2557466  6040012-604-006-678.2.21:215200-51-1_ED493ED8-...   

                       trip_headsign  direction_id  ...  delay_span  \
70819                    Duisdorf Bf             0  ...           0   
70829             Agnetendorfer Str.             0  ...           0   
70831               Endenich Nord Bf             1  ...           0   
70837    Oberkassel Süd/Römlinghoven             1  ...           0   
70838               Endenich Nord Bf             0  ...           0   
...                              ...           ...  ...         ...   
2557459  Oberkassel Süd/Römlinghoven             1  ...           0   
2557461              Oberpleis Busbf             1  ...           0   
2557463            Kopenhagener Str.             0  ...           0   
2557465              Uniklinikum Süd             1  ...           0   
2557466              Ückesdorf Mitte             1  ...           0   

         arrival_delay_span weather_int time_span_arrival  \
70819                     0           0                 0   
70829                     0           0                 0   
70831                     0           0                 0   
70837                     0           0                 0   
70838                     0           0                 0   
...                     ...         ...               ...   
2557459                   0           1                 0   
2557461                   0           1                 0   
2557463                   0           1                 0   
2557465                   0           1                 0   
2557466                   0       

In [286]:
get_stats(evening_nan_delay, ['tier_trips_count', 'tier_trips_end_at_station_count', 'nextbike_trips_count', 'nextbike_trips_end_at_station_count', 'current_temp', 'current_precipitation_volume'])

/tmp/ipykernel_2575952/41814695.py:51: RuntimeWarning: invalid value encountered in scalar divide
  qd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:55: RuntimeWarning: invalid value encountered in scalar divide
  cvqd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:51: RuntimeWarning: invalid value encountered in scalar divide
  qd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:55: RuntimeWarning: invalid value encountered in scalar divide
  cvqd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:51: RuntimeWarning: invalid value encountered in scalar divide
  qd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:55: RuntimeWarning: invalid value encountered in scalar divide
  cvqd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:51: RuntimeWarning: invalid value encountered in scalar divide
  qd = iqr / (percentile_75 + percenti

column                                        tier_trips_count  \
rows                                                     76438   
sum                                                       1510   
mean                                                  0.019755   
median                                                     0.0   
mode               0    0
Name: tier_trips_count, dtype: int64   
max                                                          5   
min                                                          0   
std_dev                                               0.157086   
variance                                              0.024676   
skewness                                               9.71915   
kurtosis                                            125.234913   
percentile_25                                              0.0   
percentile_75                                              0.0   
iqr                                                        0.0   
range                                                        5   
cv                                                    7.951902   
qd                                                         NaN   
cs                                                   61.871356   
ck                                                  797.235719   
cvs                                                  61.871356   
cvk                                                 797.235719   
cvcs                                                 61.871356   
cvck                                                797.235719   
cvcv                                                  7.951902   
cvqd                                                       NaN   
cvr                                                  253.10596   
cvm                                                        1.0   
cvmed                                                      0.0   
cvmode         0    0.0
Name: tier_trips_count, dtype: float64   

column                           tier_trips_end_at_station_count  \
rows                                                       76438   
sum                                                         1225   
mean                                                    0.016026   
median                                                       0.0   
mode           0    0
Name: tier_trips_end_at_station_count, ...   
max                                                            5   
min                                                            0   
std_dev                                                 0.139682   
variance                                                0.019511   
skewness                                               10.633013   
kurtosis                                              153.266064   
percentile_25                                                0.0   
percentile_75                                                0.0   
iqr                                                          0.0   
range                                                          5   
cv                                                      8.715932   
qd                                                           NaN   
cs                                                     76.122971   
ck                                                   1097.249523   
cvs                                                    76.122971   
cvk                                                  1097.249523   
cvcs                                                   76.122971   
cvck                                                 1097.249523   
cvcv                                                    8.715932   
cvqd                                                         NaN   
cvr                                                   311.991837   
cvm                                                          1.0   
cvmed                                                        0.0   
cvmode         0    0.0
Name: tier_trips_end_at

In [287]:
evening_nan_delay_tier = check_micromobility_datasets('tier', evening_nan_delay)

In [288]:
evening_nan_delay_tier.describe()

tier_trips_id          tier_trips_start_time  \
count   8.620000e+02                            862   
mean    8.006187e+08  2023-07-15 19:51:22.482598656   
min     7.822645e+08            2023-07-01 20:05:00   
25%     7.823741e+08            2023-07-07 20:41:15   
50%     8.086379e+08            2023-07-14 20:35:00   
75%     8.087812e+08            2023-07-24 20:50:00   
max     8.323066e+08            2023-07-31 21:55:00   
std     1.828768e+07                            NaN   

                 tier_trips_end_time              trip_duration  \
count                            862                        862   
mean   2023-07-15 20:06:22.552204288  0 days 00:15:00.069605568   
min              2023-07-01 20:15:00            0 days 00:05:00   
25%              2023-07-07 20:55:00            0 days 00:10:00   
50%              2023-07-14 20:55:00            0 days 00:10:00   
75%              2023-07-24 21:08:45            0 days 00:15:00   
max              2023-07-31 22:00:00            0 days 01:40:00   
std                              NaN  0 days 00:10:45.459074420   

       trip_distance_kilometers  trip_distance_meters  start_stop_id  \
count                862.000000            862.000000     666.000000   
mean                   1.897405           1897.405356    1227.837838   
min                    0.100719            100.718839     161.000000   
25%                    0.798073            798.072736     687.000000   
50%                    1.394682           1394.681595    1110.000000   
75%                    2.470028           2470.028305    1223.750000   
max                   11.769109          11769.109386    9039.000000   
std                    1.605697           1605.696914    1155.925004   

       end_stop_id  trip_duration_seconds  
count   452.000000             862.000000  
mean   1498.194690             900.069606  
min     161.000000             300.000000  
25%    1104.000000             600.000000  
50%    1152.000000             600.000000  
75%    1258.250000             900.000000  
max    9703.000000            6000.000000  
std    1612.589748             645.459074

In [289]:
get_stats(evening_nan_delay_tier, ['trip_duration_seconds', 'trip_distance_kilometers'])

column                                     trip_duration_seconds  \
rows                                                         862   
sum                                                     775860.0   
mean                                                  900.069606   
median                                                     600.0   
mode           0    600.0
Name: trip_duration_seconds, dtype:...   
max                                                       6000.0   
min                                                        300.0   
std_dev                                               645.459074   
variance                                           416617.416752   
skewness                                                3.779833   
kurtosis                                               20.760382   
percentile_25                                              600.0   
percentile_75                                              900.0   
iqr                                                        300.0   
range                                                     5700.0   
cv                                                      0.717121   
qd                                                           0.2   
cs                                                      0.005856   
ck                                                      0.032164   
cvs                                                     0.005856   
cvk                                                     0.032164   
cvcs                                                    0.005856   
cvck                                                    0.032164   
cvcv                                                    0.717121   
cvqd                                                         0.2   
cvr                                                     6.332844   
cvm                                                          1.0   
cvmed                                                   0.666615   
cvmode         0    0.666615
Name: trip_duration_seconds, dty...   

column                                  trip_distance_kilometers  
rows                                                         862  
sum                                                  1635.563417  
mean                                                    1.897405  
median                                                  1.394682  
mode           0       0.100719
1       0.101595
2       0.10...  
max                                                    11.769109  
min                                                     0.100719  
std_dev                                                 1.605697  
variance                                                2.578263  
skewness                                                1.767519  
kurtosis                                                4.062799  
percentile_25                                           0.798073  
percentile_75                                           2.470028  
iqr                                                     1.671956  
range                                                  11.668391  
cv                                                      0.846259  
qd                                                      0.511598  
cs                                                       1.10078  
ck                                                       2.53024  
cvs                                                      1.10078  
cvk                                                      2.53024  
cvcs                                                     1.10078  
cvck                                                     2.53024  
cvcv                                                    0.846259  
cvqd                                                    0.511598  
cvr                                                     6.149656  
cvm                                                          1.0  
cvmed                                                   0.735047  
cvmode         0

In [290]:
# get entries where trips start and end at station
evening_nan_delay_tier_station_station = evening_nan_delay_tier[evening_nan_delay_tier['end_stop_id'].notna() & evening_nan_delay_tier['start_stop_id'].notna()]
evening_nan_delay_tier_station_station

tier_trips_id tier_trips_start_time tier_trips_end_time vehicle type  \
3258480      782435847   2023-07-01 20:05:00 2023-07-01 20:15:00    e-scooter   
3125251      782334277   2023-07-01 20:05:00 2023-07-01 20:30:00    e-scooter   
2963101      782283108   2023-07-01 20:10:00 2023-07-01 20:25:00    e-scooter   
3171427      782355812   2023-07-01 20:20:00 2023-07-01 20:30:00    e-scooter   
3048678      782308675   2023-07-01 20:20:00 2023-07-01 20:30:00    e-scooter   
...                ...                   ...                 ...          ...   
3412614      832195764   2023-07-31 20:50:00 2023-07-31 21:05:00    e-scooter   
3461090      832242303   2023-07-31 20:55:00 2023-07-31 21:00:00    e-scooter   
3385595      832169884   2023-07-31 21:00:00 2023-07-31 21:10:00    e-scooter   
3416889      832199855   2023-07-31 21:10:00 2023-07-31 21:15:00    e-scooter   
3470812      832251611   2023-07-31 21:35:00 2023-07-31 21:45:00    e-scooter   

          trip_duration  trip_distance_kilometers  trip_distance_meters  \
3258480 0 days 00:10:00                  1.683868           1683.868403   
3125251 0 days 00:25:00                  5.058345           5058.345199   
2963101 0 days 00:15:00                  0.325097            325.096903   
3171427 0 days 00:10:00                  0.129378            129.377557   
3048678 0 days 00:10:00                  0.366805            366.804928   
...                 ...                       ...                   ...   
3412614 0 days 00:15:00                  2.405022           2405.021608   
3461090 0 days 00:05:00                  0.512001            512.001489   
3385595 0 days 00:10:00                  0.287767            287.767278   
3416889 0 days 00:05:00                  0.960512            960.511916   
3470812 0 days 00:10:00                  1.899547           1899.546976   

         start_stop_id                            start_stop_name  \
3258480         1221.0                          Bonn Kaufmannstr.   
3125251         1268.0                              Bonn Rheinaue   
2963101         1110.0                         Bonn Wilhelmsplatz   
3171427          694.0                     Bonn Tannenbusch Mitte   
3048678          687.0                                   Bonn Hbf   
...                ...                                        ...   
3412614          687.0                                   Bonn Hbf   
3461090          687.0                                   Bonn Hbf   
3385595         1115.0  Bonn Bertha-Von-Suttner-Pl./Beethovenhaus   
3416889         1500.0                 Bonn Konrad-Adenauer-Platz   
3470812         1131.0                             Bonn Weberstr.   

                                         start_buffer_zone  end_stop_id  \
3258480  801621     POLYGON ((7.157885983913106 50.7227...       1190.0   
3125251  801621     POLYGON ((7.157885983913106 50.7227...       1161.0   
2963101  801621     POLYGON ((7.157885983913106 50.7227...       1162.0   
3171427  801621     POLYGON ((7.157885983913106 50.7227...        694.0   
3048678  801621     POLYGON ((7.157885983913106 50.7227...       1106.0   
...                                                    ...          ...   
3412614  801621     POLYGON ((7.157885983913106 50.7227...       1235.0   
3461090  801621     POLYGON ((7.157885983913106 50.7227...       1146.0   
3385595  801621     POLYGON ((7.157885983913106 50.7227...       1111.0   
3416889  801621     POLYGON ((7.157885983913106 50.7227...       1504.0   
3470812  801621     POLYGON ((7.157885983913106 50.7227...       1221.0   

                       end_stop_name  \
3258480               Bonn Zeisigweg   
3125251            Bonn An Der Esche   
2963101                Bonn Rosental   
3171427       Bonn Tannenbusch Mitte   
3048678        Bonn Thomas-Mann-Str.   
...                              ...   
3412614              Bonn Konradstr.   
3461090                Bonn Bachstr.   
3385595  Bonn Beethovenhalle Und Swb   
34168

In [291]:
evening_nan_delay_tier_station_station.describe()

tier_trips_id          tier_trips_start_time  \
count   4.020000e+02                            402   
mean    8.007885e+08  2023-07-15 19:35:44.776119552   
min     7.822645e+08            2023-07-01 20:05:00   
25%     7.823788e+08            2023-07-07 20:26:15   
50%     8.086371e+08            2023-07-14 21:00:00   
75%     8.087819e+08            2023-07-24 20:45:00   
max     8.323066e+08            2023-07-31 21:35:00   
std     1.826239e+07                            NaN   

                 tier_trips_end_time              trip_duration  \
count                            402                        402   
mean   2023-07-15 19:49:15.223880704  0 days 00:13:30.447761194   
min              2023-07-01 20:15:00            0 days 00:05:00   
25%              2023-07-07 20:42:30            0 days 00:10:00   
50%              2023-07-14 21:07:30            0 days 00:10:00   
75%              2023-07-24 20:55:00            0 days 00:15:00   
max              2023-07-31 21:45:00            0 days 01:15:00   
std                              NaN  0 days 00:08:39.869826894   

       trip_distance_kilometers  trip_distance_meters  start_stop_id  \
count                402.000000            402.000000     402.000000   
mean                   1.610071           1610.071244    1312.101990   
min                    0.100719            100.718839     371.000000   
25%                    0.688380            688.380420     687.000000   
50%                    1.157899           1157.898621    1110.000000   
75%                    2.203613           2203.613381    1182.000000   
max                    8.743102           8743.102380    9039.000000   
std                    1.343685           1343.685439    1335.325648   

       end_stop_id  trip_duration_seconds  
count   402.000000             402.000000  
mean   1476.452736             810.447761  
min     683.000000             300.000000  
25%    1106.000000             600.000000  
50%    1153.000000             600.000000  
75%    1255.000000             900.000000  
max    9703.000000            4500.000000  
std    1540.837300             519.869827

In [292]:
# get statistics for the tier trips that start and end at a station
get_stats(evening_nan_delay_tier_station_station, ['trip_duration_seconds', 'trip_distance_kilometers'])

column                                     trip_duration_seconds  \
rows                                                         402   
sum                                                     325800.0   
mean                                                  810.447761   
median                                                     600.0   
mode           0    600.0
Name: trip_duration_seconds, dtype:...   
max                                                       4500.0   
min                                                        300.0   
std_dev                                               519.869827   
variance                                           270264.636915   
skewness                                                3.000984   
kurtosis                                               13.363427   
percentile_25                                              600.0   
percentile_75                                              900.0   
iqr                                                        300.0   
range                                                     4200.0   
cv                                                       0.64146   
qd                                                           0.2   
cs                                                      0.005773   
ck                                                      0.025705   
cvs                                                     0.005773   
cvk                                                     0.025705   
cvcs                                                    0.005773   
cvck                                                    0.025705   
cvcv                                                     0.64146   
cvqd                                                         0.2   
cvr                                                      5.18232   
cvm                                                          1.0   
cvmed                                                   0.740331   
cvmode         0    0.740331
Name: trip_duration_seconds, dty...   

column                                  trip_distance_kilometers  
rows                                                         402  
sum                                                    647.24864  
mean                                                    1.610071  
median                                                  1.157899  
mode           0      0.100719
1      0.101595
2      0.10387...  
max                                                     8.743102  
min                                                     0.100719  
std_dev                                                 1.343685  
variance                                                1.805491  
skewness                                                1.551731  
kurtosis                                                2.818788  
percentile_25                                            0.68838  
percentile_75                                           2.203613  
iqr                                                     1.515233  
range                                                   8.642384  
cv                                                       0.83455  
qd                                                      0.523941  
cs                                                      1.154832  
ck                                                      2.097804  
cvs                                                     1.154832  
cvk                                                     2.097804  
cvcs                                                    1.154832  
cvck                                                    2.097804  
cvcv                                                     0.83455  
cvqd                                                    0.523941  
cvr                                                     5.367703  
cvm                                                          1.0  
cvmed                                                    0.71916  
cvmode         0

In [293]:
evening_nan_delay_next = check_micromobility_datasets('next', evening_nan_delay)

In [294]:
evening_nan_delay_next.describe()

nextbike_trips_id      nextbike_trips_start_time  \
count       1.555000e+03                           1555   
mean        3.793712e+07  2023-07-15 15:02:59.922829824   
min         3.771653e+07            2023-07-01 20:01:00   
25%         3.782244e+07            2023-07-07 21:01:00   
50%         3.793590e+07            2023-07-14 20:01:00   
75%         3.804858e+07            2023-07-22 20:51:00   
max         3.817128e+07            2023-07-31 22:01:00   
std         1.301384e+05                            NaN   

             nextbike_trips_end_time              trip_duration  \
count                           1555                       1555   
mean   2023-07-15 15:18:22.881028864  0 days 00:15:22.958199356   
min              2023-07-01 20:11:00            0 days 00:05:00   
25%              2023-07-07 21:16:00            0 days 00:10:00   
50%              2023-07-14 20:11:00            0 days 00:15:00   
75%              2023-07-22 21:11:00            0 days 00:20:00   
max              2023-07-31 22:26:00            0 days 01:50:00   
std                              NaN  0 days 00:08:38.118062877   

       trip_distance_kilometers  trip_distance_meters  start_stop_id  \
count               1555.000000           1555.000000    1277.000000   
mean                   1.871948           1871.948110    1146.364918   
min                    0.100866            100.866433      43.000000   
25%                    0.922408            922.407833     687.000000   
50%                    1.519255           1519.255105    1112.000000   
75%                    2.399824           2399.823501    1190.000000   
max                    9.640671           9640.671235    9702.000000   
std                    1.415567           1415.567226     911.078831   

       end_stop_id  trip_duration_seconds  
count   875.000000            1555.000000  
mean   1340.654857             922.958199  
min      43.000000             300.000000  
25%    1111.000000             600.000000  
50%    1160.000000             900.000000  
75%    1224.000000            1200.000000  
max    9780.000000            6600.000000  
std    1243.646601             518.118063

In [295]:
get_stats(evening_nan_delay_next, ['trip_duration_seconds', 'trip_distance_kilometers'])

column                                     trip_duration_seconds  \
rows                                                        1555   
sum                                                    1435200.0   
mean                                                  922.958199   
median                                                     900.0   
mode           0    600.0
Name: trip_duration_seconds, dtype:...   
max                                                       6600.0   
min                                                        300.0   
std_dev                                               518.118063   
variance                                            268446.32708   
skewness                                                3.257454   
kurtosis                                               23.426094   
percentile_25                                              600.0   
percentile_75                                             1200.0   
iqr                                                        600.0   
range                                                     6300.0   
cv                                                      0.561367   
qd                                                      0.333333   
cs                                                      0.006287   
ck                                                      0.045214   
cvs                                                     0.006287   
cvk                                                     0.045214   
cvcs                                                    0.006287   
cvck                                                    0.045214   
cvcv                                                    0.561367   
cvqd                                                    0.333333   
cvr                                                     6.825878   
cvm                                                          1.0   
cvmed                                                   0.975125   
cvmode         0    0.650084
Name: trip_duration_seconds, dty...   

column                                  trip_distance_kilometers  
rows                                                        1555  
sum                                                  2910.879311  
mean                                                    1.871948  
median                                                  1.519255  
mode           0    0.982570
1    2.199943
Name: trip_distanc...  
max                                                     9.640671  
min                                                     0.100866  
std_dev                                                 1.415567  
variance                                                2.003831  
skewness                                                 1.72309  
kurtosis                                                3.858902  
percentile_25                                           0.922408  
percentile_75                                           2.399824  
iqr                                                     1.477416  
range                                                   9.539805  
cv                                                        0.7562  
qd                                                      0.444706  
cs                                                      1.217243  
ck                                                      2.726046  
cvs                                                     1.217243  
cvk                                                     2.726046  
cvcs                                                    1.217243  
cvck                                                    2.726046  
cvcv                                                      0.7562  
cvqd                                                    0.444706  
cvr                                                     5.096191  
cvm                                                          1.0  
cvmed                                                    0.81159  
cvmode         0

In [296]:
# get entries where trips start and end at station
evening_nan_delay_next_station_station = evening_nan_delay_next[evening_nan_delay_next['end_stop_id'].notna() & evening_nan_delay_next['start_stop_id'].notna()]
evening_nan_delay_next_station_station

nextbike_trips_id nextbike_trips_start_time nextbike_trips_end_time  \
1245075           37816421       2023-07-01 20:01:00     2023-07-01 20:11:00   
1318686           37853724       2023-07-01 20:06:00     2023-07-01 20:16:00   
1515605           38105105       2023-07-01 20:06:00     2023-07-01 20:46:00   
1218963           37716529       2023-07-01 20:16:00     2023-07-01 20:41:00   
1422829           38000439       2023-07-01 20:21:00     2023-07-01 20:41:00   
...                    ...                       ...                     ...   
1392716           37984594       2023-07-31 21:31:00     2023-07-31 21:46:00   
1252775           37820583       2023-07-31 21:31:00     2023-07-31 21:41:00   
1223579           37720859       2023-07-31 21:46:00     2023-07-31 21:56:00   
1329312           37892654       2023-07-31 22:01:00     2023-07-31 22:16:00   
1335610           37895414       2023-07-31 22:01:00     2023-07-31 22:16:00   

         nextbike_trips_start_at_station  nextbike_trips_end_at_station  \
1245075                            False                          False   
1318686                            False                          False   
1515605                            False                          False   
1218963                            False                          False   
1422829                            False                          False   
...                                  ...                            ...   
1392716                            False                          False   
1252775                            False                          False   
1223579                            False                          False   
1329312                             True                          False   
1335610                             True                          False   

        vehicle type   trip_duration  trip_distance_kilometers  \
1245075         bike 0 days 00:10:00                  3.114978   
1318686         bike 0 days 00:10:00                  0.100866   
1515605         bike 0 days 00:40:00                  7.408574   
1218963         bike 0 days 00:25:00                  2.825435   
1422829         bike 0 days 00:20:00                  2.699145   
...              ...             ...                       ...   
1392716         bike 0 days 00:15:00                  2.389327   
1252775         bike 0 days 00:10:00                  0.935837   
1223579         bike 0 days 00:10:00                  1.151484   
1329312         bike 0 days 00:15:00                  1.645817   
1335610         bike 0 days 00:15:00                  1.831696   

         trip_distance_meters  \
1245075           3114.978233   
1318686            100.866433   
1515605           7408.574406   
1218963           2825.434827   
1422829           2699.145397   
...                       ...   
1392716           2389.326515   
1252775            935.836836   
1223579           1151.483630   
1329312           1645.816542   
1335610           1831.695734   

                                            start_location  \
1245075  b'\x01\x01\x00\x00\x00R\x0f\xd1\xe8\x0eb\x1c@\...   
1318686  b'\x01\x01\x00\x00\x00\x85\xcf\xd6\xc1\xc1\x8e...   
1515605  b'\x01\x01\x00\x00\x00\xa7Z\x0b\xb3\xd0\x8e\x1...   
1218963  b'\x01\x01\x00\x00\x00\xf6\xed$"\xfc[\x1c@\xfb...   
1422829  b'\x01\x01\x00\x00\x00\xffA$C\x8e]\x1c@4\xbf\x...   
...                                                    ...   
1392716  b'\x01\x01\x00\x00\x00\xac\xc9SV\xd3e\x1c@+MJA...   
1252775  b'\x01\x01\x00\x00\x00I\xa2\x97Q,g\x1c@\x1e\xc...   
1223579  b'\x01\x01\x00\x00\x00\xa7 ?\x1b\xb9~\x1c@\x9a...   
1329312  b'\x01\x01\x00\x00\x00|H\xf8\xde\xdf`\x1c@/\xe...   
1335610  b'\x01\x01\x00\x00\x00\xeb;\xbf(A/\x1c@i\xfd-\...   

                                              end_location  start_stop_id  \
1245075  b'\x01\x01\x00\x00\x00]j\x84~\xa6~\x1c@E+\xf7\...         1102.0   
1318686  b'\x01\x01\x00\x00\x00\nj\xf8\x16\xd6\x8d\x1c@...

In [297]:
evening_nan_delay_next_station_station.describe()

nextbike_trips_id      nextbike_trips_start_time  \
count       7.610000e+02                            761   
mean        3.794043e+07  2023-07-15 17:30:12.851510784   
min         3.771653e+07            2023-07-01 20:01:00   
25%         3.782492e+07            2023-07-07 21:06:00   
50%         3.793888e+07            2023-07-14 20:26:00   
75%         3.805421e+07            2023-07-22 20:16:00   
max         3.817128e+07            2023-07-31 22:01:00   
std         1.306728e+05                            NaN   

             nextbike_trips_end_time              trip_duration  \
count                            761                        761   
mean   2023-07-15 17:44:19.237844992  0 days 00:14:06.386333771   
min              2023-07-01 20:11:00            0 days 00:05:00   
25%              2023-07-07 21:21:00            0 days 00:10:00   
50%              2023-07-14 20:46:00            0 days 00:15:00   
75%              2023-07-22 20:31:00            0 days 00:15:00   
max              2023-07-31 22:16:00            0 days 01:50:00   
std                              NaN  0 days 00:08:16.637857071   

       trip_distance_kilometers  trip_distance_meters  start_stop_id  \
count                761.000000            761.000000     761.000000   
mean                   1.562615           1562.615472    1185.822602   
min                    0.100866            100.866433      43.000000   
25%                    0.791171            791.171279     688.000000   
50%                    1.254460           1254.459733    1115.000000   
75%                    1.932509           1932.508700    1182.000000   
max                    9.640671           9640.671235    9702.000000   
std                    1.219393           1219.392681     990.946906   

       end_stop_id  trip_duration_seconds  
count   761.000000             761.000000  
mean   1361.869908             846.386334  
min     161.000000             300.000000  
25%    1112.000000             600.000000  
50%    1160.000000             900.000000  
75%    1223.000000             900.000000  
max    9780.000000            6600.000000  
std    1270.535926             496.637857

In [298]:
# get statistics for the tier trips that start and end at a station
get_stats(evening_nan_delay_next_station_station, ['trip_duration_seconds', 'trip_distance_kilometers'])

column                                     trip_duration_seconds  \
rows                                                         761   
sum                                                     644100.0   
mean                                                  846.386334   
median                                                     900.0   
mode           0    600.0
Name: trip_duration_seconds, dtype:...   
max                                                       6600.0   
min                                                        300.0   
std_dev                                               496.637857   
variance                                           246649.161076   
skewness                                                4.663434   
kurtosis                                               43.950066   
percentile_25                                              600.0   
percentile_75                                              900.0   
iqr                                                        300.0   
range                                                     6300.0   
cv                                                      0.586774   
qd                                                           0.2   
cs                                                       0.00939   
ck                                                      0.088495   
cvs                                                      0.00939   
cvk                                                     0.088495   
cvcs                                                     0.00939   
cvck                                                    0.088495   
cvcv                                                    0.586774   
cvqd                                                         0.2   
cvr                                                     7.443409   
cvm                                                          1.0   
cvmed                                                   1.063344   
cvmode         0    0.708896
Name: trip_duration_seconds, dty...   

column                                  trip_distance_kilometers  
rows                                                         761  
sum                                                  1189.150374  
mean                                                    1.562615  
median                                                   1.25446  
mode           0    0.98257
Name: trip_distance_kilometers, d...  
max                                                     9.640671  
min                                                     0.100866  
std_dev                                                 1.219393  
variance                                                1.486919  
skewness                                                2.197744  
kurtosis                                                7.343652  
percentile_25                                           0.791171  
percentile_75                                           1.932509  
iqr                                                     1.141337  
range                                                   9.539805  
cv                                                      0.780354  
qd                                                      0.419042  
cs                                                      1.802327  
ck                                                      6.022385  
cvs                                                     1.802327  
cvk                                                     6.022385  
cvcs                                                    1.802327  
cvck                                                    6.022385  
cvcv                                                    0.780354  
cvqd                                                    0.419042  
cvr                                                     6.105024  
cvm                                                          1.0  
cvmed                                                   0.802795  
cvmode         0

In [299]:
evening_delay.describe()

route_id     agency_id    route_type    service_id  direction_id  \
count  82723.000000  82723.000000  82723.000000  82723.000000  82723.000000   
mean     564.094762      6.001692      2.756223   2371.522358      0.508927   
min       60.000000      6.000000      0.000000      3.000000      0.000000   
25%      602.000000      6.000000      3.000000     43.000000      0.000000   
50%      606.000000      6.000000      3.000000     64.000000      1.000000   
75%      611.000000      6.000000      3.000000     64.000000      1.000000   
max      640.000000      8.000000      3.000000  27313.000000      1.000000   
std      150.967812      0.058155      0.819703   7537.485171      0.499923   

           shape_id      stop_id            actual_arrival_time  \
count  82723.000000  82723.00000                          80690   
mean    3567.711036   2310.82462  2023-07-17 02:26:45.401165312   
min        6.000000     43.00000            2023-07-01 19:59:50   
25%     1918.000000   1212.00000            2023-07-09 20:44:00   
50%     2717.000000   1431.00000            2023-07-17 20:58:30   
75%     5377.000000   1682.00000            2023-07-24 20:21:45   
max    10365.000000   9780.00000            2023-07-31 22:00:00   
std     2684.584249   2409.94414                            NaN   

               actual_departure_time  vrs_timestamp  ...  \
count                          82723   82723.000000  ...   
mean   2023-07-17 02:53:25.530384128  195491.089564  ...   
min              2023-07-01 20:00:10  175805.000000  ...   
25%              2023-07-09 20:41:30  185804.000000  ...   
50%              2023-07-17 21:01:45  193304.000000  ...   
75%              2023-07-24 20:28:15  201804.000000  ...   
max              2023-07-31 22:00:45  224807.000000  ...   
std                              NaN   10803.775646  ...   

       departure_delay_float actual_arrival_time_float  \
count           82723.000000              82723.000000   
mean                0.619479             201986.715907   
min                 0.166667                  0.000000   
25%                 0.250000             202030.000000   
50%                 0.500000             204815.000000   
75%                 0.750000             212415.000000   
max                24.000000             220000.000000   
std                 1.170489              32498.988321   

      actual_departure_time_float arrival_delay_span   weather_int  \
count                82723.000000            82723.0  82723.000000   
mean                207053.218694                0.0      0.200851   
min                 200010.000000                0.0      0.000000   
25%                 202230.000000                0.0      0.000000   
50%                 204930.000000                0.0      0.000000   
75%                 212515.000000                0.0      0.000000   
max                 220045.000000                0.0      2.000000   
std                   5372.863190                0.0      0.445554   

       time_span_int_arrival       weekend  time_span_int  delay_category  \
count           82723.000000  82723.000000   82723.000000    82723.000000   
mean                5.850574      0.794398       5.997969        0.632654   
min                 0.000000      0.000000       0.000000       -1.000000   
25%                 6.000000      0.000000       6.000000        0.000000   
50%                 6.000000      0.000000       6.000000        1.000000   
75%                 6.000000      2.000000       6.000000        1.000000   
max                 6.000000      3.000000       6.000000        1.000000   
std                 0.934200      1.076930       0.110369        0.530621   

       cancelled_trip  
count         82723.0  
mean              0.0  
min               0.0  
25%               0.0  
50%               0.0  
75%               0.0  
max               0.0  
std               0.0  

[8 rows x 38 columns]

In [300]:
evening_no_delay.describe()

route_id     agency_id    route_type    service_id  direction_id  \
count  54395.000000  54395.000000  54395.000000  54395.000000  54395.000000   
mean     545.884603      6.917419      2.554481   5224.430370      0.470117   
min       16.000000      1.000000      0.000000      3.000000      0.000000   
25%      551.000000      6.000000      3.000000     43.000000      0.000000   
50%      606.000000      6.000000      3.000000     64.000000      0.000000   
75%      612.000000      6.000000      3.000000    151.000000      1.000000   
max      884.000000     12.000000      3.000000  28777.000000      1.000000   
std      224.142584      2.054570      1.066813  10649.196349      0.499111   

           shape_id       stop_id            actual_arrival_time  \
count  54395.000000  54395.000000                          40193   
mean    4272.747183   2161.707381  2023-07-17 01:19:01.793098240   
min        6.000000     43.000000            2023-07-01 19:59:00   
25%     2014.000000   1175.000000            2023-07-09 20:24:45   
50%     3858.000000   1433.000000            2023-07-17 21:11:45   
75%     6391.000000   1702.000000            2023-07-24 20:14:45   
max    10365.000000   9780.000000            2023-07-31 21:59:00   
std     2869.523052   2286.204377                            NaN   

               actual_departure_time  vrs_timestamp  ...  \
count                          54395   54395.000000  ...   
mean   2023-07-17 01:47:20.506204672  195487.325839  ...   
min              2023-07-01 20:00:00  175805.000000  ...   
25%              2023-07-09 20:19:00  185805.000000  ...   
50%              2023-07-17 21:05:00  193305.000000  ...   
75%              2023-07-24 20:28:00  201804.000000  ...   
max              2023-07-31 22:00:00  224807.000000  ...   
std                              NaN   10458.064112  ...   

       departure_delay_float actual_arrival_time_float  \
count           54395.000000              54395.000000   
mean                0.032817             152988.736649   
min                 0.000000                  0.000000   
25%                 0.000000                  0.000000   
50%                 0.000000             202945.000000   
75%                 0.000000             211200.000000   
max                24.000000             220000.000000   
std                 0.365268              91061.988431   

      actual_departure_time_float arrival_delay_span   weather_int  \
count                54395.000000            54395.0  54395.000000   
mean                207078.941355                0.0      0.196213   
min                 200000.000000                0.0      0.000000   
25%                 202200.000000                0.0      0.000000   
50%                 205000.000000                0.0      0.000000   
75%                 212400.000000                0.0      0.000000   
max                 220000.000000                0.0      2.000000   
std                   5368.552391                0.0      0.443167   

       time_span_int_arrival       weekend  time_span_int  delay_category  \
count           54395.000000  54395.000000   54395.000000    54395.000000   
mean                4.425572      0.790771       5.997242       -0.254362   
min                 0.000000      0.000000       0.000000       -1.000000   
25%                 0.000000      0.000000       6.000000       -1.000000   
50%                 6.000000      0.000000       6.000000        0.000000   
75%                 6.000000      2.000000       6.000000        0.000000   
max                 6.000000      3.000000       6.000000        1.000000   
std                 2.632716      1.068746       0.128601        0.450691   

       cancelled_trip  
count         54395.0  
mean              0.0  
min               0.0  
25%               0.0  
50%               0.0  
75%               0.0  
max               0.0  
std               0.0  

[8 rows x 38 columns]

In [301]:
evening_nan_delay.describe()

route_id     agency_id    route_type    service_id  direction_id  \
count  76438.000000  76438.000000  76438.000000  76438.000000  76438.000000   
mean     536.640715      6.161386      2.605288   3609.782543      0.489364   
min       16.000000      1.000000      0.000000      3.000000      0.000000   
25%      601.000000      6.000000      3.000000     43.000000      0.000000   
50%      606.000000      6.000000      3.000000     64.000000      0.000000   
75%      611.000000      6.000000      3.000000    130.000000      1.000000   
max      884.000000     12.000000      3.000000  29132.000000      1.000000   
std      191.258504      0.881473      1.014077   9091.246167      0.499890   

           shape_id       stop_id actual_arrival_time actual_departure_time  \
count  76438.000000  76438.000000                   0                     0   
mean    4038.795220   2225.870810                 NaT                   NaT   
min        6.000000     43.000000                 NaT                   NaT   
25%     1985.000000   1204.000000                 NaT                   NaT   
50%     2936.000000   1455.000000                 NaT                   NaT   
75%     6129.000000   1681.000000                 NaT                   NaT   
max    10365.000000   9780.000000                 NaT                   NaT   
std     2841.335745   2320.573798                 NaN                   NaN   

       vrs_timestamp  ...  departure_delay_float actual_arrival_time_float  \
count   76438.000000  ...                    0.0                   76438.0   
mean   192636.003938  ...                    NaN                       0.0   
min    152806.000000  ...                    NaN                       0.0   
25%    190304.000000  ...                    NaN                       0.0   
50%    193303.000000  ...                    NaN                       0.0   
75%    195803.000000  ...                    NaN                       0.0   
max    223805.000000  ...                    NaN                       0.0   
std      7732.983348  ...                    NaN                       0.0   

      actual_departure_time_float arrival_delay_span   weather_int  \
count                     76438.0            76438.0  76438.000000   
mean                          0.0                0.0      0.204401   
min                           0.0                0.0      0.000000   
25%                           0.0                0.0      0.000000   
50%                           0.0                0.0      0.000000   
75%                           0.0                0.0      0.000000   
max                           0.0                0.0      2.000000   
std                           0.0                0.0      0.462048   

       time_span_int_arrival       weekend  time_span_int  delay_category  \
count                76438.0  76438.000000        76438.0         76438.0   
mean                     0.0      0.826448            0.0            -1.0   
min                      0.0      0.000000            0.0            -1.0   
25%                      0.0      0.000000            0.0            -1.0   
50%                      0.0      0.000000            0.0            -1.0   
75%                      0.0      2.000000            0.0            -1.0   
max                      0.0      3.000000            0.0            -1.0   
std                      0.0      1.083203            0.0             0.0   

       cancelled_trip  
count         76438.0  
mean              1.0  
min               1.0  
25%               1.0  
50%               1.0  
75%               1.0  
max               1.0  
std               0.0  

[8 rows x 38 columns]

#### Night

In [302]:
night_delay = delay[(delay['scheduled_arrival_time'].dt.hour >= 22) | (delay['scheduled_arrival_time'].dt.hour <= 2)]
night_delay

route_id  agency_id route_short_name  route_type route_type_name  \
0             551          8              551           3             Bus   
1             551          8              551           3             Bus   
2             551          8              551           3             Bus   
3             551          8              551           3             Bus   
4             551          8              551           3             Bus   
...           ...        ...              ...         ...             ...   
2564753       683          6               N3           3             Bus   
2564754       684          6               N4           3             Bus   
2564755       690          6              N10           3             Bus   
2564756       685          6               N5           3             Bus   
2564758       687          6               N7           3             Bus   

                                      agency_name  service_id  \
0        RSVG Rhein-Sieg-Verkehrsgesellschaft mbH         125   
1        RSVG Rhein-Sieg-Verkehrsgesellschaft mbH         125   
2        RSVG Rhein-Sieg-Verkehrsgesellschaft mbH         125   
3        RSVG Rhein-Sieg-Verkehrsgesellschaft mbH         125   
4        RSVG Rhein-Sieg-Verkehrsgesellschaft mbH         125   
...                                           ...         ...   
2564753         SWB Stadtwerke Bonn Verkehrs GmbH         179   
2564754         SWB Stadtwerke Bonn Verkehrs GmbH         179   
2564755         SWB Stadtwerke Bonn Verkehrs GmbH         179   
2564756         SWB Stadtwerke Bonn Verkehrs GmbH         179   
2564758         SWB Stadtwerke Bonn Verkehrs GmbH         179   

                                                   trip_id  \
0        93-551-008-687.2.36:014000-33-157_49E69401-92E...   
1        93-551-008-687.2.36:014000-33-157_49E69401-92E...   
2        93-551-008-687.2.36:014000-33-157_49E69401-92E...   
3        93-551-008-687.2.36:014000-33-157_49E69401-92E...   
4        93-551-008-687.2.36:014000-33-157_49E69401-92E...   
...                                                    ...   
2564753  6830009-683-006-687.2.35:263500-37-1_CF84035F-...   
2564754  6840005-684-006-687.2.32:263500-36-1_7F56FE12-...   
2564755  6900005-690-006-687.2.25:263500-30-1_AC8C2160-...   
2564756  6850009-685-006-687.2.21:263500-36-1_BE11DA3E-...   
2564758  6870005-687-006-687.2.24:263500-34-1_F0CE2D00-...   

                           trip_headsign  direction_id  ...  delay_span  \
0                           Troisdorf Bf             0  ...           0   
1                           Troisdorf Bf             0  ...           0   
2                           Troisdorf Bf             0  ...           0   
3                           Troisdorf Bf             0  ...           0   
4                           Troisdorf Bf             0  ...           0   
...                                  ...           ...  ...         ...   
2564753  Hochkreuz/Deutsches Museum Bonn             0  ...         0-5   
2564754                      Am Waldrand             0  ...         0-5   
2564755                        Pappelweg             0  ...         0-5   
2564756                  Ückesdorf Mitte             0  ...        5-10   
2564758    Bad Godesberg Bf / Rheinallee             0  ...         0-5   

         arrival_delay_span weather_int time_span_arrival  \
0                         0           0                 0   
1                         0           0                 0   
2                         0           0                 0   
3                         0           0                 0   
4                         0           0                 0   
...                     ...         ...               ...   
2564753                   0           1                 0   
2564754                   0           1                 0   
2564755                   0           1                 0   
2564756                   0           1     ear

In [303]:
get_stats(night_delay, ['tier_trips_count', 'tier_trips_end_at_station_count', 'nextbike_trips_count', 'nextbike_trips_end_at_station_count', 'current_temp', 'current_precipitation_volume'])

/tmp/ipykernel_2575952/41814695.py:51: RuntimeWarning: invalid value encountered in scalar divide
  qd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:55: RuntimeWarning: invalid value encountered in scalar divide
  cvqd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:51: RuntimeWarning: invalid value encountered in scalar divide
  qd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:55: RuntimeWarning: invalid value encountered in scalar divide
  cvqd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:51: RuntimeWarning: invalid value encountered in scalar divide
  qd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:55: RuntimeWarning: invalid value encountered in scalar divide
  cvqd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:51: RuntimeWarning: invalid value encountered in scalar divide
  qd = iqr / (percentile_75 + percenti

column                                        tier_trips_count  \
rows                                                     95607   
sum                                                        815   
mean                                                  0.008524   
median                                                     0.0   
mode               0    0
Name: tier_trips_count, dtype: int64   
max                                                          4   
min                                                          0   
std_dev                                                 0.1044   
variance                                              0.010899   
skewness                                             14.746896   
kurtosis                                            270.471701   
percentile_25                                              0.0   
percentile_75                                              0.0   
iqr                                                        0.0   
range                                                        4   
cv                                                    12.24713   
qd                                                         NaN   
cs                                                   141.25323   
ck                                                 2590.714744   
cvs                                                  141.25323   
cvk                                                2590.714744   
cvcs                                                 141.25323   
cvck                                               2590.714744   
cvcv                                                  12.24713   
cvqd                                                       NaN   
cvr                                                  469.23681   
cvm                                                        1.0   
cvmed                                                      0.0   
cvmode         0    0.0
Name: tier_trips_count, dtype: float64   

column                           tier_trips_end_at_station_count  \
rows                                                       95607   
sum                                                          695   
mean                                                    0.007269   
median                                                       0.0   
mode           0    0
Name: tier_trips_end_at_station_count, ...   
max                                                            4   
min                                                            0   
std_dev                                                 0.096481   
variance                                                0.009308   
skewness                                               16.113926   
kurtosis                                              326.144576   
percentile_25                                                0.0   
percentile_75                                                0.0   
iqr                                                          0.0   
range                                                          4   
cv                                                     13.272251   
qd                                                           NaN   
cs                                                    167.017382   
ck                                                   3380.418471   
cvs                                                   167.017382   
cvk                                                  3380.418471   
cvcs                                                  167.017382   
cvck                                                 3380.418471   
cvcv                                                   13.272251   
cvqd                                                         NaN   
cvr                                                   550.256115   
cvm                                                          1.0   
cvmed                                                        0.0   
cvmode         0    0.0
Name: tier_trips_end_at

In [304]:
night_delay_tier = check_micromobility_datasets('tier', night_delay)

In [305]:
night_delay_tier.describe()

tier_trips_id          tier_trips_start_time  \
count   5.830000e+02                            583   
mean    8.009293e+08  2023-07-15 22:25:04.631217664   
min     7.822654e+08            2023-06-30 01:45:00   
25%     7.823842e+08            2023-07-07 23:05:00   
50%     8.086414e+08            2023-07-14 23:45:00   
75%     8.087676e+08            2023-07-23 00:07:30   
max     8.323115e+08            2023-08-01 01:45:00   
std     1.833358e+07                            NaN   

                 tier_trips_end_time              trip_duration  \
count                            583                        583   
mean   2023-07-15 22:40:38.696398080  0 days 00:15:34.065180102   
min              2023-06-30 02:05:00            0 days 00:05:00   
25%              2023-07-07 23:17:30            0 days 00:10:00   
50%              2023-07-14 23:55:00            0 days 00:15:00   
75%              2023-07-23 00:32:30            0 days 00:20:00   
max              2023-08-01 02:05:00            0 days 01:45:00   
std                              NaN  0 days 00:10:29.546099405   

       trip_distance_kilometers  trip_distance_meters  start_stop_id  \
count                583.000000            583.000000     456.000000   
mean                   2.109089           2109.088830    1452.701754   
min                    0.101267            101.267318     161.000000   
25%                    0.950041            950.041212    1110.000000   
50%                    1.787106           1787.106290    1142.000000   
75%                    2.835616           2835.616119    1294.250000   
max                   10.501190          10501.189675    9702.000000   
std                    1.515924           1515.924233    1271.000936   

       end_stop_id  trip_duration_seconds  
count    332.00000             583.000000  
mean    1547.25000             934.065180  
min      161.00000             300.000000  
25%     1110.00000             600.000000  
50%     1161.00000             900.000000  
75%     1431.00000            1200.000000  
max     9703.00000            6300.000000  
std     1635.43838             629.546099

In [306]:
get_stats(night_delay_tier, ['trip_duration_seconds', 'trip_distance_kilometers'])

column                                     trip_duration_seconds  \
rows                                                         583   
sum                                                     544560.0   
mean                                                   934.06518   
median                                                     900.0   
mode           0    600.0
Name: trip_duration_seconds, dtype:...   
max                                                       6300.0   
min                                                        300.0   
std_dev                                               629.546099   
variance                                           396328.291277   
skewness                                                3.468558   
kurtosis                                               20.709624   
percentile_25                                              600.0   
percentile_75                                             1200.0   
iqr                                                        600.0   
range                                                     6000.0   
cv                                                      0.673985   
qd                                                      0.333333   
cs                                                       0.00551   
ck                                                      0.032896   
cvs                                                      0.00551   
cvk                                                     0.032896   
cvcs                                                     0.00551   
cvck                                                    0.032896   
cvcv                                                    0.673985   
cvqd                                                    0.333333   
cvr                                                     6.423535   
cvm                                                          1.0   
cvmed                                                    0.96353   
cvmode         0    0.642353
Name: trip_duration_seconds, dty...   

column                                  trip_distance_kilometers  
rows                                                         583  
sum                                                  1229.598788  
mean                                                    2.109089  
median                                                  1.787106  
mode           0       0.101267
1       0.105014
2       0.10...  
max                                                     10.50119  
min                                                     0.101267  
std_dev                                                 1.515924  
variance                                                2.298026  
skewness                                                1.525467  
kurtosis                                                4.123491  
percentile_25                                           0.950041  
percentile_75                                           2.835616  
iqr                                                     1.885575  
range                                                  10.399922  
cv                                                      0.718758  
qd                                                      0.498084  
cs                                                      1.006295  
ck                                                      2.720117  
cvs                                                     1.006295  
cvk                                                     2.720117  
cvcs                                                    1.006295  
cvck                                                    2.720117  
cvcv                                                    0.718758  
cvqd                                                    0.498084  
cvr                                                     4.931003  
cvm                                                          1.0  
cvmed                                                   0.847336  
cvmode         0

In [307]:
# get entries where trips start and end at station
night_delay_tier_station_station = night_delay_tier[night_delay_tier['end_stop_id'].notna() & night_delay_tier['start_stop_id'].notna()]
night_delay_tier_station_station

tier_trips_id tier_trips_start_time tier_trips_end_time vehicle type  \
3171653      782356027   2023-06-30 01:45:00 2023-06-30 02:05:00    e-scooter   
3209527      782391260   2023-07-01 01:45:00 2023-07-01 01:50:00    e-scooter   
3210269      782391943   2023-07-01 01:45:00 2023-07-01 01:50:00    e-scooter   
3202039      782383788   2023-07-01 22:05:00 2023-07-01 22:15:00    e-scooter   
3086182      782321553   2023-07-01 22:10:00 2023-07-01 22:25:00    e-scooter   
...                ...                   ...                 ...          ...   
3422531      832205256   2023-07-31 23:25:00 2023-08-01 00:00:00    e-scooter   
3485603      832265823   2023-07-31 23:25:00 2023-08-01 00:00:00    e-scooter   
3398184      832181971   2023-08-01 00:10:00 2023-08-01 00:20:00    e-scooter   
3326567      832125594   2023-08-01 01:45:00 2023-08-01 02:05:00    e-scooter   
3464513      832245595   2023-08-01 01:45:00 2023-08-01 02:05:00    e-scooter   

          trip_duration  trip_distance_kilometers  trip_distance_meters  \
3171653 0 days 00:20:00                  3.598056           3598.055590   
3209527 0 days 00:05:00                  0.670973            670.973151   
3210269 0 days 00:05:00                  0.838693            838.692953   
3202039 0 days 00:10:00                  0.960059            960.058958   
3086182 0 days 00:15:00                  3.410649           3410.649100   
...                 ...                       ...                   ...   
3422531 0 days 00:35:00                  1.787106           1787.106290   
3485603 0 days 00:35:00                  1.774445           1774.445116   
3398184 0 days 00:10:00                  0.649892            649.892254   
3326567 0 days 00:20:00                  0.308480            308.479763   
3464513 0 days 00:20:00                  0.288030            288.030156   

         start_stop_id                            start_stop_name  \
3171653          687.0                                   Bonn Hbf   
3209527         1115.0  Bonn Bertha-Von-Suttner-Pl./Beethovenhaus   
3210269         1115.0  Bonn Bertha-Von-Suttner-Pl./Beethovenhaus   
3202039         1102.0                         Bonn Friedensplatz   
3086182         2535.0                             Bonn Im Bonnet   
...                ...                                        ...   
3422531         1153.0                              Bonn Heerstr.   
3485603         1153.0                              Bonn Heerstr.   
3398184         1255.0                Bonn Graf-Stauffenberg-Str.   
3326567         1115.0  Bonn Bertha-Von-Suttner-Pl./Beethovenhaus   
3464513         1115.0  Bonn Bertha-Von-Suttner-Pl./Beethovenhaus   

                                         start_buffer_zone  end_stop_id  \
3171653  801621     POLYGON ((7.157885983913106 50.7227...       1406.0   
3209527  801621     POLYGON ((7.157885983913106 50.7227...        687.0   
3210269  801621     POLYGON ((7.157885983913106 50.7227...        687.0   
3202039  801621     POLYGON ((7.157885983913106 50.7227...       1153.0   
3086182  801621     POLYGON ((7.157885983913106 50.7227...       1502.0   
...                                                    ...          ...   
3422531  801621     POLYGON ((7.157885983913106 50.7227...       1190.0   
3485603  801621     POLYGON ((7.157885983913106 50.7227...       1190.0   
3398184  801621     POLYGON ((7.157885983913106 50.7227...       6994.0   
3326567  801621     POLYGON ((7.157885983913106 50.7227...       1111.0   
3464513  801621     POLYGON ((7.157885983913106 50.7227...       1111.0   

                       end_stop_name  \
3171653       Bonn Kopenhagener Str.   
3209527                     Bonn Hbf   
3210269                     Bonn Hbf   
3202039                Bonn Heerstr.   
3086182   Bonn Beueler Bahnhofsplatz   
...                              ...   
3422531               Bonn Zeisigweg   
3485603               Bonn Zeisigweg   
3398184  Bonn Heinrich-Lützeler-Str.   
33265

In [308]:
night_delay_tier_station_station.describe()

tier_trips_id          tier_trips_start_time  \
count   2.970000e+02                            297   
mean    8.015016e+08  2023-07-16 13:11:42.020201984   
min     7.822654e+08            2023-06-30 01:45:00   
25%     7.823909e+08            2023-07-07 23:55:00   
50%     8.086478e+08            2023-07-15 00:40:00   
75%     8.087760e+08            2023-07-23 22:20:00   
max     8.323115e+08            2023-08-01 01:45:00   
std     1.823595e+07                            NaN   

                 tier_trips_end_time              trip_duration  \
count                            297                        297   
mean   2023-07-16 13:26:23.030302976  0 days 00:14:41.010101010   
min              2023-06-30 02:05:00            0 days 00:05:00   
25%              2023-07-08 00:15:00            0 days 00:10:00   
50%              2023-07-15 00:45:00            0 days 00:10:00   
75%              2023-07-23 23:10:00            0 days 00:15:00   
max              2023-08-01 02:05:00            0 days 01:10:00   
std                              NaN  0 days 00:09:19.145393295   

       trip_distance_kilometers  trip_distance_meters  start_stop_id  \
count                297.000000            297.000000     297.000000   
mean                   1.839963           1839.962911    1368.824916   
min                    0.105014            105.013611     684.000000   
25%                    0.837488            837.487616    1106.000000   
50%                    1.700072           1700.071750    1115.000000   
75%                    2.642716           2642.716216    1240.000000   
max                    6.171166           6171.166311    9702.000000   
std                    1.279936           1279.935848    1023.190722   

       end_stop_id  trip_duration_seconds  
count   297.000000             297.000000  
mean   1627.117845             881.010101  
min     683.000000             300.000000  
25%    1115.000000             600.000000  
50%    1172.000000             600.000000  
75%    1500.000000             900.000000  
max    9703.000000            4200.000000  
std    1709.317187             559.145393

In [309]:
# get statistics for the tier trips that start and end at a station
get_stats(night_delay_tier_station_station, ['trip_duration_seconds', 'trip_distance_kilometers'])

column                                     trip_duration_seconds  \
rows                                                         297   
sum                                                     261660.0   
mean                                                  881.010101   
median                                                     600.0   
mode           0    600.0
Name: trip_duration_seconds, dtype:...   
max                                                       4200.0   
min                                                        300.0   
std_dev                                               559.145393   
variance                                           312643.570844   
skewness                                                2.359292   
kurtosis                                                7.712071   
percentile_25                                              600.0   
percentile_75                                              900.0   
iqr                                                        300.0   
range                                                     3900.0   
cv                                                      0.634664   
qd                                                           0.2   
cs                                                      0.004219   
ck                                                      0.013793   
cvs                                                     0.004219   
cvk                                                     0.013793   
cvcs                                                    0.004219   
cvck                                                    0.013793   
cvcv                                                    0.634664   
cvqd                                                         0.2   
cvr                                                     4.426737   
cvm                                                          1.0   
cvmed                                                   0.681036   
cvmode         0    0.681036
Name: trip_duration_seconds, dty...   

column                                  trip_distance_kilometers  
rows                                                         297  
sum                                                   546.468985  
mean                                                    1.839963  
median                                                  1.700072  
mode           0      0.105014
1      0.109334
2      0.11436...  
max                                                     6.171166  
min                                                     0.105014  
std_dev                                                 1.279936  
variance                                                1.638236  
skewness                                                0.889894  
kurtosis                                                0.543321  
percentile_25                                           0.837488  
percentile_75                                           2.642716  
iqr                                                     1.805229  
range                                                   6.066153  
cv                                                      0.695631  
qd                                                      0.518713  
cs                                                      0.695265  
ck                                                      0.424491  
cvs                                                     0.695265  
cvk                                                     0.424491  
cvcs                                                    0.695265  
cvck                                                    0.424491  
cvcv                                                    0.695631  
cvqd                                                    0.518713  
cvr                                                     3.296889  
cvm                                                          1.0  
cvmed                                                   0.923971  
cvmode         0

In [310]:
night_delay_next = check_micromobility_datasets('next', evening_delay)

In [311]:
night_delay_next.describe()

nextbike_trips_id      nextbike_trips_start_time  \
count       1.568000e+03                           1568   
mean        3.793780e+07  2023-07-16 12:25:58.737244672   
min         3.771653e+07            2023-07-01 20:01:00   
25%         3.782706e+07            2023-07-08 21:23:30   
50%         3.793750e+07            2023-07-15 20:41:00   
75%         3.804722e+07            2023-07-22 21:36:00   
max         3.817169e+07            2023-07-31 22:01:00   
std         1.285777e+05                            NaN   

             nextbike_trips_end_time              trip_duration  \
count                           1568                       1568   
mean   2023-07-16 12:41:46.454081792  0 days 00:15:47.716836734   
min              2023-07-01 20:11:00            0 days 00:05:00   
25%              2023-07-08 21:39:45            0 days 00:10:00   
50%              2023-07-15 20:48:30            0 days 00:15:00   
75%              2023-07-22 22:01:00            0 days 00:20:00   
max              2023-07-31 22:31:00            0 days 02:00:00   
std                              NaN  0 days 00:10:24.861963710   

       trip_distance_kilometers  trip_distance_meters  start_stop_id  \
count               1568.000000           1568.000000    1216.000000   
mean                   1.879000           1878.999607    1266.750000   
min                    0.100920            100.920160     161.000000   
25%                    0.856356            856.356069    1103.000000   
50%                    1.538932           1538.932316    1140.000000   
75%                    2.461684           2461.684104    1224.000000   
max                   13.022949          13022.949077    8950.000000   
std                    1.486588           1486.588465     959.090928   

       end_stop_id  trip_duration_seconds  
count   885.000000            1568.000000  
mean   1387.512994             947.716837  
min     161.000000             300.000000  
25%    1110.000000             600.000000  
50%    1153.000000             900.000000  
75%    1223.000000            1200.000000  
max    9780.000000            7200.000000  
std    1334.718523             624.861964

In [312]:
get_stats(night_delay_next, ['trip_duration_seconds', 'trip_distance_kilometers'])

column                                     trip_duration_seconds  \
rows                                                        1568   
sum                                                    1486020.0   
mean                                                  947.716837   
median                                                     900.0   
mode           0    600.0
Name: trip_duration_seconds, dtype:...   
max                                                       7200.0   
min                                                        300.0   
std_dev                                               624.861964   
variance                                           390452.473692   
skewness                                                4.031047   
kurtosis                                               27.262882   
percentile_25                                              600.0   
percentile_75                                             1200.0   
iqr                                                        600.0   
range                                                     6900.0   
cv                                                      0.659334   
qd                                                      0.333333   
cs                                                      0.006451   
ck                                                       0.04363   
cvs                                                     0.006451   
cvk                                                      0.04363   
cvcs                                                    0.006451   
cvck                                                     0.04363   
cvcv                                                    0.659334   
cvqd                                                    0.333333   
cvr                                                     7.280656   
cvm                                                          1.0   
cvmed                                                   0.949651   
cvmode         0    0.6331
Name: trip_duration_seconds, dtype...   

column                                  trip_distance_kilometers  
rows                                                        1568  
sum                                                  2946.271384  
mean                                                       1.879  
median                                                  1.538932  
mode           0    0.110127
1    2.199943
Name: trip_distanc...  
max                                                    13.022949  
min                                                      0.10092  
std_dev                                                 1.486588  
variance                                                2.209945  
skewness                                                2.043639  
kurtosis                                                6.751446  
percentile_25                                           0.856356  
percentile_75                                           2.461684  
iqr                                                     1.605328  
range                                                  12.922029  
cv                                                       0.79116  
qd                                                      0.483818  
cs                                                      1.374717  
ck                                                       4.54157  
cvs                                                     1.374717  
cvk                                                      4.54157  
cvcs                                                    1.374717  
cvck                                                     4.54157  
cvcv                                                     0.79116  
cvqd                                                    0.483818  
cvr                                                     6.877079  
cvm                                                          1.0  
cvmed                                                   0.819017  
cvmode         0

In [313]:
# get entries where trips start and end at station
night_delay_next_station_station = night_delay_next[night_delay_next['end_stop_id'].notna() & night_delay_next['start_stop_id'].notna()]
night_delay_next_station_station

nextbike_trips_id nextbike_trips_start_time nextbike_trips_end_time  \
1298316           37844432       2023-07-01 20:01:00     2023-07-01 20:21:00   
1421214           37998824       2023-07-01 20:01:00     2023-07-01 20:11:00   
1245075           37816421       2023-07-01 20:01:00     2023-07-01 20:11:00   
1218963           37716529       2023-07-01 20:16:00     2023-07-01 20:41:00   
1553014           38099832       2023-07-01 20:26:00     2023-07-01 20:41:00   
...                    ...                       ...                     ...   
1641137           37772556       2023-07-31 21:31:00     2023-07-31 21:46:00   
1332556           37860355       2023-07-31 21:31:00     2023-07-31 22:31:00   
1540818           38089733       2023-07-31 21:41:00     2023-07-31 21:46:00   
1223579           37720859       2023-07-31 21:46:00     2023-07-31 21:56:00   
1329312           37892654       2023-07-31 22:01:00     2023-07-31 22:16:00   

         nextbike_trips_start_at_station  nextbike_trips_end_at_station  \
1298316                            False                          False   
1421214                            False                           True   
1245075                            False                          False   
1218963                            False                          False   
1553014                            False                          False   
...                                  ...                            ...   
1641137                            False                          False   
1332556                            False                          False   
1540818                            False                           True   
1223579                            False                          False   
1329312                             True                          False   

        vehicle type   trip_duration  trip_distance_kilometers  \
1298316         bike 0 days 00:20:00                  2.689943   
1421214         bike 0 days 00:10:00                  0.580338   
1245075         bike 0 days 00:10:00                  3.114978   
1218963         bike 0 days 00:25:00                  2.825435   
1553014         bike 0 days 00:15:00                  0.929504   
...              ...             ...                       ...   
1641137         bike 0 days 00:15:00                  1.109057   
1332556         bike 0 days 01:00:00                  2.772292   
1540818         bike 0 days 00:05:00                  0.112330   
1223579         bike 0 days 00:10:00                  1.151484   
1329312         bike 0 days 00:15:00                  1.645817   

         trip_distance_meters  \
1298316           2689.943386   
1421214            580.338181   
1245075           3114.978233   
1218963           2825.434827   
1553014            929.503629   
...                       ...   
1641137           1109.057430   
1332556           2772.291604   
1540818            112.330142   
1223579           1151.483630   
1329312           1645.816542   

                                            start_location  \
1298316  b'\x01\x01\x00\x00\x00\x02\x10w\xf5*R\x1c@j\x1...   
1421214  b'\x01\x01\x00\x00\x00\xf3\x92\xff\xc9\xdf}\x1...   
1245075  b'\x01\x01\x00\x00\x00R\x0f\xd1\xe8\x0eb\x1c@\...   
1218963  b'\x01\x01\x00\x00\x00\xf6\xed$"\xfc[\x1c@\xfb...   
1553014  b'\x01\x01\x00\x00\x00\xf1\x9e\x03\xcb\x11b\x1...   
...                                                    ...   
1641137  b'\x01\x01\x00\x00\x00\x8e\x02D\xc1\x8cY\x1c@Q...   
1332556  b'\x01\x01\x00\x00\x00Z\x0f_&\x8a0\x1c@\x00\x8...   
1540818  b'\x01\x01\x00\x00\x00\xb5\x8bi\xa6{]\x1c@\xd7...   
1223579  b'\x01\x01\x00\x00\x00\xa7 ?\x1b\xb9~\x1c@\x9a...   
1329312  b'\x01\x01\x00\x00\x00|H\xf8\xde\xdf`\x1c@/\xe...   

                                              end_location  start_stop_id  \
1298316  b'\x01\x01\x00\x00\x00\x7f\x16K\x91|e\x1c@\x88...         1231.0   
1421214  b'\x01\x01\x00\x00\x00/1\x96\xe9\x97x\x1c@\x86...

In [314]:
night_delay_next_station_station.describe()

nextbike_trips_id      nextbike_trips_start_time  \
count       7.390000e+02                            739   
mean        3.793823e+07  2023-07-15 18:51:41.001352960   
min         3.771653e+07            2023-07-01 20:01:00   
25%         3.782730e+07            2023-07-08 20:36:00   
50%         3.793560e+07            2023-07-14 21:01:00   
75%         3.804554e+07            2023-07-21 21:06:00   
max         3.817169e+07            2023-07-31 22:01:00   
std         1.283279e+05                            NaN   

             nextbike_trips_end_time              trip_duration  \
count                            739                        739   
mean   2023-07-15 19:05:53.098782208  0 days 00:14:12.097428958   
min              2023-07-01 20:11:00            0 days 00:05:00   
25%              2023-07-08 20:51:00            0 days 00:10:00   
50%              2023-07-14 21:16:00            0 days 00:10:00   
75%              2023-07-21 21:16:00            0 days 00:15:00   
max              2023-07-31 22:31:00            0 days 02:00:00   
std                              NaN  0 days 00:09:32.665816018   

       trip_distance_kilometers  trip_distance_meters  start_stop_id  \
count                739.000000            739.000000     739.000000   
mean                   1.529174           1529.174352    1331.815968   
min                    0.100920            100.920160     161.000000   
25%                    0.739921            739.921483    1103.000000   
50%                    1.241755           1241.754916    1140.000000   
75%                    1.968413           1968.413009    1223.000000   
max                    9.640671           9640.671235    8507.000000   
std                    1.195923           1195.923221    1106.684830   

       end_stop_id  trip_duration_seconds  
count   739.000000             739.000000  
mean   1423.359946             852.097429  
min     161.000000             300.000000  
25%    1112.000000             600.000000  
50%    1160.000000             600.000000  
75%    1223.000000             900.000000  
max    9780.000000            7200.000000  
std    1406.463053             572.665816

In [315]:
# get statistics for the tier trips that start and end at a station
get_stats(night_delay_next_station_station, ['trip_duration_seconds', 'trip_distance_kilometers'])

column                                     trip_duration_seconds  \
rows                                                         739   
sum                                                     629700.0   
mean                                                  852.097429   
median                                                     600.0   
mode           0    600.0
Name: trip_duration_seconds, dtype:...   
max                                                       7200.0   
min                                                        300.0   
std_dev                                               572.665816   
variance                                           327946.136836   
skewness                                                5.105904   
kurtosis                                               44.312995   
percentile_25                                              600.0   
percentile_75                                              900.0   
iqr                                                        300.0   
range                                                     6900.0   
cv                                                      0.672066   
qd                                                           0.2   
cs                                                      0.008916   
ck                                                       0.07738   
cvs                                                     0.008916   
cvk                                                      0.07738   
cvcs                                                    0.008916   
cvck                                                     0.07738   
cvcv                                                    0.672066   
cvqd                                                         0.2   
cvr                                                     8.097666   
cvm                                                          1.0   
cvmed                                                   0.704145   
cvmode         0    0.704145
Name: trip_duration_seconds, dty...   

column                                  trip_distance_kilometers  
rows                                                         739  
sum                                                  1130.059846  
mean                                                    1.529174  
median                                                  1.241755  
mode           0    0.110127
Name: trip_distance_kilometers, ...  
max                                                     9.640671  
min                                                      0.10092  
std_dev                                                 1.195923  
variance                                                1.430232  
skewness                                                2.002379  
kurtosis                                                6.553317  
percentile_25                                           0.739921  
percentile_75                                           1.968413  
iqr                                                     1.228492  
range                                                   9.539751  
cv                                                      0.782071  
qd                                                      0.453597  
cs                                                      1.674337  
ck                                                      5.479714  
cvs                                                     1.674337  
cvk                                                     5.479714  
cvcs                                                    1.674337  
cvck                                                    5.479714  
cvcv                                                    0.782071  
cvqd                                                    0.453597  
cvr                                                     6.238498  
cvm                                                          1.0  
cvmed                                                   0.812043  
cvmode         0

In [316]:
night_no_delay = no_delay[(no_delay['scheduled_arrival_time'].dt.hour >= 22) | (no_delay['scheduled_arrival_time'].dt.hour <= 2)]
night_no_delay

route_id  agency_id route_short_name  route_type route_type_name  \
0             551          8              551           3             Bus   
1             551          8              551           3             Bus   
2             551          8              551           3             Bus   
3             551          8              551           3             Bus   
4             551          8              551           3             Bus   
...           ...        ...              ...         ...             ...   
2564740       687          6               N7           3             Bus   
2564747       685          6               N5           3             Bus   
2564751       690          6              N10           3             Bus   
2564752       687          6               N7           3             Bus   
2564757       684          6               N4           3             Bus   

                                      agency_name  service_id  \
0        RSVG Rhein-Sieg-Verkehrsgesellschaft mbH         125   
1        RSVG Rhein-Sieg-Verkehrsgesellschaft mbH         125   
2        RSVG Rhein-Sieg-Verkehrsgesellschaft mbH         125   
3        RSVG Rhein-Sieg-Verkehrsgesellschaft mbH         125   
4        RSVG Rhein-Sieg-Verkehrsgesellschaft mbH         125   
...                                           ...         ...   
2564740         SWB Stadtwerke Bonn Verkehrs GmbH         179   
2564747         SWB Stadtwerke Bonn Verkehrs GmbH         179   
2564751         SWB Stadtwerke Bonn Verkehrs GmbH         179   
2564752         SWB Stadtwerke Bonn Verkehrs GmbH         179   
2564757         SWB Stadtwerke Bonn Verkehrs GmbH         179   

                                                   trip_id  \
0        93-551-008-687.2.36:014000-33-157_49E69401-92E...   
1        93-551-008-687.2.36:014000-33-157_49E69401-92E...   
2        93-551-008-687.2.36:014000-33-157_49E69401-92E...   
3        93-551-008-687.2.36:014000-33-157_49E69401-92E...   
4        93-551-008-687.2.36:014000-33-157_49E69401-92E...   
...                                                    ...   
2564740  6870005-687-006-687.2.24:263500-34-1_F0CE2D00-...   
2564747  6850009-685-006-687.2.21:263500-36-1_BE11DA3E-...   
2564751  6900005-690-006-687.2.25:263500-30-1_AC8C2160-...   
2564752  6870005-687-006-687.2.24:263500-34-1_F0CE2D00-...   
2564757  6840005-684-006-687.2.32:263500-36-1_7F56FE12-...   

                         trip_headsign  direction_id  ...  delay_span  \
0                         Troisdorf Bf             0  ...           0   
1                         Troisdorf Bf             0  ...           0   
2                         Troisdorf Bf             0  ...           0   
3                         Troisdorf Bf             0  ...           0   
4                         Troisdorf Bf             0  ...           0   
...                                ...           ...  ...         ...   
2564740  Bad Godesberg Bf / Rheinallee             0  ...           0   
2564747                Ückesdorf Mitte             0  ...           0   
2564751                      Pappelweg             0  ...           0   
2564752  Bad Godesberg Bf / Rheinallee             0  ...           0   
2564757                    Am Waldrand             0  ...           0   

         arrival_delay_span weather_int time_span_arrival  \
0                         0           0                 0   
1                         0           0                 0   
2                         0           0                 0   
3                         0           0                 0   
4                         0           0                 0   
...                     ...         ...               ...   
2564740                   0           1                 0   
2564747                   0           1                 0   
2564751                   0           1                 0   
2564752                   0           1                 0   
2564757   

In [317]:
get_stats(night_no_delay, ['tier_trips_count', 'tier_trips_end_at_station_count', 'nextbike_trips_count', 'nextbike_trips_end_at_station_count', 'current_temp', 'current_precipitation_volume'])

/tmp/ipykernel_2575952/41814695.py:51: RuntimeWarning: invalid value encountered in scalar divide
  qd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:55: RuntimeWarning: invalid value encountered in scalar divide
  cvqd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:51: RuntimeWarning: invalid value encountered in scalar divide
  qd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:55: RuntimeWarning: invalid value encountered in scalar divide
  cvqd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:51: RuntimeWarning: invalid value encountered in scalar divide
  qd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:55: RuntimeWarning: invalid value encountered in scalar divide
  cvqd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:51: RuntimeWarning: invalid value encountered in scalar divide
  qd = iqr / (percentile_75 + percenti

column                                        tier_trips_count  \
rows                                                     60743   
sum                                                       1534   
mean                                                  0.025254   
median                                                     0.0   
mode               0    0
Name: tier_trips_count, dtype: int64   
max                                                          5   
min                                                          0   
std_dev                                               0.202275   
variance                                              0.040915   
skewness                                             11.400167   
kurtosis                                            177.611311   
percentile_25                                              0.0   
percentile_75                                              0.0   
iqr                                                        0.0   
range                                                        5   
cv                                                    8.009627   
qd                                                         NaN   
cs                                                   56.359847   
ck                                                  878.070141   
cvs                                                  56.359847   
cvk                                                 878.070141   
cvcs                                                 56.359847   
cvck                                                878.070141   
cvcv                                                  8.009627   
cvqd                                                       NaN   
cvr                                                 197.988918   
cvm                                                        1.0   
cvmed                                                      0.0   
cvmode         0    0.0
Name: tier_trips_count, dtype: float64   

column                           tier_trips_end_at_station_count  \
rows                                                       60743   
sum                                                         1275   
mean                                                     0.02099   
median                                                       0.0   
mode           0    0
Name: tier_trips_end_at_station_count, ...   
max                                                            5   
min                                                            0   
std_dev                                                 0.178263   
variance                                                0.031778   
skewness                                               11.511596   
kurtosis                                              177.578758   
percentile_25                                                0.0   
percentile_75                                                0.0   
iqr                                                          0.0   
range                                                          5   
cv                                                      8.492722   
qd                                                           NaN   
cs                                                     64.576527   
ck                                                    996.162448   
cvs                                                    64.576527   
cvk                                                   996.162448   
cvcs                                                   64.576527   
cvck                                                  996.162448   
cvcv                                                    8.492722   
cvqd                                                         NaN   
cvr                                                   238.207843   
cvm                                                          1.0   
cvmed                                                        0.0   
cvmode         0    0.0
Name: tier_trips_end_at

In [318]:
night_no_delay_tier = check_micromobility_datasets('tier', night_no_delay)

In [319]:
night_no_delay_tier.describe()

tier_trips_id          tier_trips_start_time  \
count   6.630000e+02                            663   
mean    8.002677e+08  2023-07-15 18:12:46.153846272   
min     7.822653e+08            2023-06-30 01:45:00   
25%     7.823766e+08            2023-07-07 23:17:30   
50%     8.086415e+08            2023-07-14 23:15:00   
75%     8.087676e+08            2023-07-22 23:02:30   
max     8.323080e+08            2023-08-01 00:10:00   
std     1.752843e+07                            NaN   

                 tier_trips_end_time              trip_duration  \
count                            663                        663   
mean   2023-07-15 18:28:06.877828096  0 days 00:15:20.723981900   
min              2023-06-30 02:05:00            0 days 00:05:00   
25%              2023-07-07 23:32:30            0 days 00:10:00   
50%              2023-07-14 23:30:00            0 days 00:15:00   
75%              2023-07-22 23:25:00            0 days 00:20:00   
max              2023-08-01 00:20:00            0 days 02:00:00   
std                              NaN  0 days 00:10:31.493281903   

       trip_distance_kilometers  trip_distance_meters  start_stop_id  \
count                663.000000            663.000000     538.000000   
mean                   2.203113           2203.112799    1038.498141   
min                    0.106863            106.863116     161.000000   
25%                    1.003615           1003.615494     687.000000   
50%                    1.776377           1776.376654    1102.000000   
75%                    3.012621           3012.620567    1151.000000   
max                    9.699347           9699.347396    9039.000000   
std                    1.627383           1627.382589     790.371389   

       end_stop_id  trip_duration_seconds  
count   346.000000             663.000000  
mean   1551.447977             920.723982  
min     161.000000             300.000000  
25%    1115.000000             600.000000  
50%    1173.000000             900.000000  
75%    1432.500000            1200.000000  
max    9029.000000            7200.000000  
std    1524.950753             631.493282

In [320]:
get_stats(night_no_delay_tier, ['trip_duration_seconds', 'trip_distance_kilometers'])

column                                     trip_duration_seconds  \
rows                                                         663   
sum                                                     610440.0   
mean                                                  920.723982   
median                                                     900.0   
mode           0    600.0
Name: trip_duration_seconds, dtype:...   
max                                                       7200.0   
min                                                        300.0   
std_dev                                               631.493282   
variance                                           398783.765089   
skewness                                                4.359941   
kurtosis                                               29.873697   
percentile_25                                              600.0   
percentile_75                                             1200.0   
iqr                                                        600.0   
range                                                     6900.0   
cv                                                      0.685866   
qd                                                      0.333333   
cs                                                      0.006904   
ck                                                      0.047306   
cvs                                                     0.006904   
cvk                                                     0.047306   
cvcs                                                    0.006904   
cvck                                                    0.047306   
cvcv                                                    0.685866   
cvqd                                                    0.333333   
cvr                                                     7.494103   
cvm                                                          1.0   
cvmed                                                   0.977492   
cvmode         0    0.651661
Name: trip_duration_seconds, dty...   

column                                  trip_distance_kilometers  
rows                                                         663  
sum                                                  1460.663786  
mean                                                    2.203113  
median                                                  1.776377  
mode           0      0.106863
1      0.107249
2      0.11604...  
max                                                     9.699347  
min                                                     0.106863  
std_dev                                                 1.627383  
variance                                                2.648374  
skewness                                                1.371718  
kurtosis                                                2.147056  
percentile_25                                           1.003615  
percentile_75                                           3.012621  
iqr                                                     2.009005  
range                                                   9.592484  
cv                                                      0.738674  
qd                                                      0.500221  
cs                                                      0.842898  
ck                                                      1.319331  
cvs                                                     0.842898  
cvk                                                     1.319331  
cvcs                                                    0.842898  
cvck                                                    1.319331  
cvcv                                                    0.738674  
cvqd                                                    0.500221  
cvr                                                      4.35406  
cvm                                                          1.0  
cvmed                                                   0.806303  
cvmode         0

In [321]:
# get entries where trips start and end at station
night_no_delay_tier_station_station = night_no_delay_tier[night_no_delay_tier['end_stop_id'].notna() & night_no_delay_tier['start_stop_id'].notna()]
night_no_delay_tier_station_station

tier_trips_id tier_trips_start_time tier_trips_end_time vehicle type  \
3171653      782356027   2023-06-30 01:45:00 2023-06-30 02:05:00    e-scooter   
3209527      782391260   2023-07-01 01:45:00 2023-07-01 01:50:00    e-scooter   
3210269      782391943   2023-07-01 01:45:00 2023-07-01 01:50:00    e-scooter   
3254146      782431910   2023-07-01 01:50:00 2023-07-01 02:00:00    e-scooter   
3200599      782382352   2023-07-01 22:00:00 2023-07-01 22:20:00    e-scooter   
...                ...                   ...                 ...          ...   
3485596      832265817   2023-07-31 22:25:00 2023-07-31 22:45:00    e-scooter   
3518645      832297525   2023-07-31 22:55:00 2023-07-31 23:00:00    e-scooter   
3318827      832120317   2023-07-31 23:10:00 2023-08-01 00:20:00    e-scooter   
3421744      832204504   2023-07-31 23:15:00 2023-07-31 23:25:00    e-scooter   
3398184      832181971   2023-08-01 00:10:00 2023-08-01 00:20:00    e-scooter   

          trip_duration  trip_distance_kilometers  trip_distance_meters  \
3171653 0 days 00:20:00                  3.598056           3598.055590   
3209527 0 days 00:05:00                  0.670973            670.973151   
3210269 0 days 00:05:00                  0.838693            838.692953   
3254146 0 days 00:10:00                  1.779253           1779.253071   
3200599 0 days 00:20:00                  2.149035           2149.035440   
...                 ...                       ...                   ...   
3485596 0 days 00:20:00                  1.171579           1171.578745   
3518645 0 days 00:05:00                  0.704362            704.361980   
3318827 0 days 01:10:00                  0.117849            117.848655   
3421744 0 days 00:10:00                  1.002491           1002.491082   
3398184 0 days 00:10:00                  0.649892            649.892254   

         start_stop_id                            start_stop_name  \
3171653          687.0                                   Bonn Hbf   
3209527         1115.0  Bonn Bertha-Von-Suttner-Pl./Beethovenhaus   
3210269         1115.0  Bonn Bertha-Von-Suttner-Pl./Beethovenhaus   
3254146          687.0                                   Bonn Hbf   
3200599          687.0                                   Bonn Hbf   
...                ...                                        ...   
3485596          686.0                     Bonn Universität/Markt   
3518645         1115.0  Bonn Bertha-Von-Suttner-Pl./Beethovenhaus   
3318827         1115.0  Bonn Bertha-Von-Suttner-Pl./Beethovenhaus   
3421744         1504.0                              Bonn Beuel Bf   
3398184         1255.0                Bonn Graf-Stauffenberg-Str.   

                                         start_buffer_zone  end_stop_id  \
3171653  801621     POLYGON ((7.157885983913106 50.7227...       1406.0   
3209527  801621     POLYGON ((7.157885983913106 50.7227...        687.0   
3210269  801621     POLYGON ((7.157885983913106 50.7227...        687.0   
3254146  801621     POLYGON ((7.157885983913106 50.7227...        688.0   
3200599  801621     POLYGON ((7.157885983913106 50.7227...       1177.0   
...                                                    ...          ...   
3485596  801621     POLYGON ((7.157885983913106 50.7227...       1153.0   
3518645  801621     POLYGON ((7.157885983913106 50.7227...       1161.0   
3318827  801621     POLYGON ((7.157885983913106 50.7227...       1115.0   
3421744  801621     POLYGON ((7.157885983913106 50.7227...       1126.0   
3398184  801621     POLYGON ((7.157885983913106 50.7227...       6994.0   

                                     end_stop_name  \
3171653                     Bonn Kopenhagener Str.   
3209527                                   Bonn Hbf   
3210269                                   Bonn Hbf   
3254146                                  Bonn West   
3200599                      Bonn Innenministerium   
...                                            ...   
3485596                    

In [322]:
night_no_delay_tier_station_station.describe()

tier_trips_id          tier_trips_start_time  \
count   3.160000e+02                            316   
mean    7.998285e+08  2023-07-15 13:54:08.924050432   
min     7.822653e+08            2023-06-30 01:45:00   
25%     7.823612e+08            2023-07-07 23:08:45   
50%     8.086317e+08            2023-07-14 22:40:00   
75%     8.087761e+08            2023-07-22 23:40:00   
max     8.323066e+08            2023-08-01 00:10:00   
std     1.766611e+07                            NaN   

                 tier_trips_end_time              trip_duration  \
count                            316                        316   
mean   2023-07-15 14:09:03.037974784  0 days 00:14:54.113924050   
min              2023-06-30 02:05:00            0 days 00:05:00   
25%              2023-07-07 23:18:45            0 days 00:10:00   
50%              2023-07-14 23:02:30            0 days 00:15:00   
75%              2023-07-22 23:51:15            0 days 00:15:00   
max              2023-08-01 00:20:00            0 days 01:35:00   
std                              NaN  0 days 00:10:06.233890373   

       trip_distance_kilometers  trip_distance_meters  start_stop_id  \
count                316.000000            316.000000     316.000000   
mean                   1.941445           1941.445171    1041.879747   
min                    0.106863            106.863116     686.000000   
25%                    0.916781            916.781259     687.000000   
50%                    1.628878           1628.878345    1102.000000   
75%                    2.620320           2620.319798    1137.250000   
max                    6.761793           6761.793236    9039.000000   
std                    1.405865           1405.864852     700.619733   

       end_stop_id  trip_duration_seconds  
count   316.000000             316.000000  
mean   1608.775316             894.113924  
min     683.000000             300.000000  
25%    1115.000000             600.000000  
50%    1175.000000             900.000000  
75%    1500.000000             900.000000  
max    9029.000000            5700.000000  
std    1579.856679             606.233890

In [323]:
# get statistics for the tier trips that start and end at a station
get_stats(night_no_delay_tier_station_station, ['trip_duration_seconds', 'trip_distance_kilometers'])

column                                     trip_duration_seconds  \
rows                                                         316   
sum                                                     282540.0   
mean                                                  894.113924   
median                                                     900.0   
mode           0    600.0
Name: trip_duration_seconds, dtype:...   
max                                                       5700.0   
min                                                        300.0   
std_dev                                                606.23389   
variance                                           367519.529837   
skewness                                                3.541344   
kurtosis                                                19.24479   
percentile_25                                              600.0   
percentile_75                                              900.0   
iqr                                                        300.0   
range                                                     5400.0   
cv                                                      0.678028   
qd                                                           0.2   
cs                                                      0.005842   
ck                                                      0.031745   
cvs                                                     0.005842   
cvk                                                     0.031745   
cvcs                                                    0.005842   
cvck                                                    0.031745   
cvcv                                                    0.678028   
cvqd                                                         0.2   
cvr                                                     6.039499   
cvm                                                          1.0   
cvmed                                                   1.006583   
cvmode         0    0.671055
Name: trip_duration_seconds, dty...   

column                                  trip_distance_kilometers  
rows                                                         316  
sum                                                   613.496674  
mean                                                    1.941445  
median                                                  1.628878  
mode           0      0.106863
1      0.107249
2      0.11604...  
max                                                     6.761793  
min                                                     0.106863  
std_dev                                                 1.405865  
variance                                                1.976456  
skewness                                                1.044249  
kurtosis                                                0.777753  
percentile_25                                           0.916781  
percentile_75                                            2.62032  
iqr                                                     1.703539  
range                                                    6.65493  
cv                                                      0.724133  
qd                                                       0.48162  
cs                                                       0.74278  
ck                                                       0.55322  
cvs                                                      0.74278  
cvk                                                      0.55322  
cvcs                                                     0.74278  
cvck                                                     0.55322  
cvcv                                                    0.724133  
cvqd                                                     0.48162  
cvr                                                     3.427823  
cvm                                                          1.0  
cvmed                                                   0.839003  
cvmode         0

In [324]:
night_no_delay_next = check_micromobility_datasets('next', evening_no_delay)

In [325]:
night_no_delay_next.describe()

nextbike_trips_id      nextbike_trips_start_time  \
count       1.305000e+03                           1305   
mean        3.794256e+07  2023-07-16 05:42:43.172413696   
min         3.771653e+07            2023-07-01 20:11:00   
25%         3.783094e+07            2023-07-08 20:16:00   
50%         3.794729e+07            2023-07-15 20:16:00   
75%         3.805036e+07            2023-07-22 20:51:00   
max         3.817077e+07            2023-07-31 21:56:00   
std         1.282935e+05                            NaN   

             nextbike_trips_end_time              trip_duration  \
count                           1305                       1305   
mean   2023-07-16 05:58:03.356321792  0 days 00:15:20.183908045   
min              2023-07-01 20:21:00            0 days 00:05:00   
25%              2023-07-08 20:26:00            0 days 00:10:00   
50%              2023-07-15 20:31:00            0 days 00:15:00   
75%              2023-07-22 21:11:00            0 days 00:20:00   
max              2023-07-31 22:06:00            0 days 01:30:00   
std                              NaN  0 days 00:08:21.944650743   

       trip_distance_kilometers  trip_distance_meters  start_stop_id  \
count               1305.000000           1305.000000    1090.000000   
mean                   1.884745           1884.745043    1071.053211   
min                    0.100920            100.920160     161.000000   
25%                    0.939460            939.459929     687.000000   
50%                    1.511361           1511.360928    1103.000000   
75%                    2.387797           2387.797312    1160.000000   
max                   13.022949          13022.949077    9780.000000   
std                    1.470614           1470.613797     863.457136   

       end_stop_id  trip_duration_seconds  
count   732.000000            1305.000000  
mean   1310.622951             920.183908  
min     161.000000             300.000000  
25%    1113.750000             600.000000  
50%    1160.000000             900.000000  
75%    1223.000000            1200.000000  
max    9702.000000            5400.000000  
std    1090.739184             501.944651

In [326]:
get_stats(night_no_delay_next, ['trip_duration_seconds', 'trip_distance_kilometers'])

column                                     trip_duration_seconds  \
rows                                                        1305   
sum                                                    1200840.0   
mean                                                  920.183908   
median                                                     900.0   
mode           0    600.0
Name: trip_duration_seconds, dtype:...   
max                                                       5400.0   
min                                                        300.0   
std_dev                                               501.944651   
variance                                            251948.43241   
skewness                                                2.912494   
kurtosis                                               17.262957   
percentile_25                                              600.0   
percentile_75                                             1200.0   
iqr                                                        600.0   
range                                                     5100.0   
cv                                                      0.545483   
qd                                                      0.333333   
cs                                                      0.005802   
ck                                                      0.034392   
cvs                                                     0.005802   
cvk                                                     0.034392   
cvcs                                                    0.005802   
cvck                                                    0.034392   
cvcv                                                    0.545483   
cvqd                                                    0.333333   
cvr                                                      5.54237   
cvm                                                          1.0   
cvmed                                                   0.978065   
cvmode         0    0.652044
Name: trip_duration_seconds, dty...   

column                                  trip_distance_kilometers  
rows                                                        1305  
sum                                                  2459.592281  
mean                                                    1.884745  
median                                                  1.511361  
mode           0    0.98257
Name: trip_distance_kilometers, d...  
max                                                    13.022949  
min                                                      0.10092  
std_dev                                                 1.470614  
variance                                                2.162705  
skewness                                                2.151608  
kurtosis                                                6.840153  
percentile_25                                            0.93946  
percentile_75                                           2.387797  
iqr                                                     1.448337  
range                                                  12.922029  
cv                                                      0.780272  
qd                                                      0.435295  
cs                                                      1.463068  
ck                                                      4.651223  
cvs                                                     1.463068  
cvk                                                     4.651223  
cvcs                                                    1.463068  
cvck                                                    4.651223  
cvcv                                                    0.780272  
cvqd                                                    0.435295  
cvr                                                     6.856115  
cvm                                                          1.0  
cvmed                                                   0.801891  
cvmode         0

In [327]:
# get entries where trips start and end at station
night_no_delay_next_station_station = night_no_delay_next[night_no_delay_next['end_stop_id'].notna() & night_no_delay_next['start_stop_id'].notna()]
night_no_delay_next_station_station

nextbike_trips_id nextbike_trips_start_time nextbike_trips_end_time  \
1218963           37716529       2023-07-01 20:16:00     2023-07-01 20:41:00   
1649771           37781190       2023-07-01 20:21:00     2023-07-01 20:31:00   
1361050           37933936       2023-07-01 20:26:00     2023-07-01 20:36:00   
1588995           38130455       2023-07-01 20:36:00     2023-07-01 20:51:00   
1436917           38008727       2023-07-01 20:41:00     2023-07-01 21:16:00   
...                    ...                       ...                     ...   
1469167           38033725       2023-07-31 21:26:00     2023-07-31 21:36:00   
1540817           38089732       2023-07-31 21:26:00     2023-07-31 21:41:00   
1392716           37984594       2023-07-31 21:31:00     2023-07-31 21:46:00   
1258227           37738223       2023-07-31 21:31:00     2023-07-31 21:41:00   
1670611           37802030       2023-07-31 21:56:00     2023-07-31 22:06:00   

         nextbike_trips_start_at_station  nextbike_trips_end_at_station  \
1218963                            False                          False   
1649771                            False                          False   
1361050                             True                          False   
1588995                            False                          False   
1436917                            False                          False   
...                                  ...                            ...   
1469167                            False                          False   
1540817                            False                          False   
1392716                            False                          False   
1258227                            False                          False   
1670611                            False                          False   

        vehicle type   trip_duration  trip_distance_kilometers  \
1218963         bike 0 days 00:25:00                  2.825435   
1649771         bike 0 days 00:10:00                  0.574793   
1361050         bike 0 days 00:10:00                  0.784946   
1588995         bike 0 days 00:15:00                  1.988363   
1436917         bike 0 days 00:35:00                  6.703541   
...              ...             ...                       ...   
1469167         bike 0 days 00:10:00                  0.939808   
1540817         bike 0 days 00:15:00                  1.422846   
1392716         bike 0 days 00:15:00                  2.389327   
1258227         bike 0 days 00:10:00                  1.822654   
1670611         bike 0 days 00:10:00                  1.127301   

         trip_distance_meters  \
1218963           2825.434827   
1649771            574.792584   
1361050            784.946180   
1588995           1988.362862   
1436917           6703.540950   
...                       ...   
1469167            939.808209   
1540817           1422.846299   
1392716           2389.326515   
1258227           1822.654198   
1670611           1127.301066   

                                            start_location  \
1218963  b'\x01\x01\x00\x00\x00\xf6\xed$"\xfc[\x1c@\xfb...   
1649771  b'\x01\x01\x00\x00\x00\x18\xd2\xe1!\x8c_\x1c@J...   
1361050  b'\x01\x01\x00\x00\x00\xf4\x8a\xa7\x1ei`\x1c@c...   
1588995  b'\x01\x01\x00\x00\x00\x9d\xd7\xd8%\xaag\x1c@\...   
1436917  b'\x01\x01\x00\x00\x00\xc5:U\xbegd\x1c@\x8b\xf...   
...                                                    ...   
1469167  b'\x01\x01\x00\x00\x00|\xb9O\x8e\x02d\x1c@\xf6...   
1540817  b'\x01\x01\x00\x00\x00\x04\xacU\xbb&d\x1c@\xaf...   
1392716  b'\x01\x01\x00\x00\x00\xac\xc9SV\xd3e\x1c@+MJA...   
1258227  b'\x01\x01\x00\x00\x00\x17\x9c\xc1\xdf/V\x1c@\...   
1670611  b'\x01\x01\x00\x00\x00\xe7\xfc\x14\xc7\x81g\x1...   

                                              end_location  start_stop_id  \
1218963  b'\x01\x01\x00\x00\x00\xddC\xc2\xf7\xfef\x1c@\...         1182.0   
1649771  b'\x01\x01\x00\x00\x00\xaf@\xf4\xa4LZ\x1c@\xbc...

In [328]:
night_no_delay_next_station_station.describe()

nextbike_trips_id      nextbike_trips_start_time  \
count       6.430000e+02                            643   
mean        3.794369e+07  2023-07-15 16:32:30.699844352   
min         3.771653e+07            2023-07-01 20:16:00   
25%         3.782470e+07            2023-07-07 21:23:30   
50%         3.795065e+07            2023-07-14 20:21:00   
75%         3.805476e+07            2023-07-21 21:23:30   
max         3.817077e+07            2023-07-31 21:56:00   
std         1.324728e+05                            NaN   

             nextbike_trips_end_time              trip_duration  \
count                            643                        643   
mean   2023-07-15 16:46:19.595645440  0 days 00:13:48.895800933   
min              2023-07-01 20:31:00            0 days 00:05:00   
25%              2023-07-07 21:38:30            0 days 00:10:00   
50%              2023-07-14 20:41:00            0 days 00:15:00   
75%              2023-07-21 21:36:00            0 days 00:15:00   
max              2023-07-31 22:06:00            0 days 01:00:00   
std                              NaN  0 days 00:06:44.306097641   

       trip_distance_kilometers  trip_distance_meters  start_stop_id  \
count                643.000000            643.000000     643.000000   
mean                   1.541099           1541.099334    1114.262830   
min                    0.100920            100.920160     161.000000   
25%                    0.825008            825.007810     687.000000   
50%                    1.247518           1247.517568    1106.000000   
75%                    1.929398           1929.398245    1161.000000   
max                    9.640671           9640.671235    9780.000000   
std                    1.141667           1141.666591     890.969753   

       end_stop_id  trip_duration_seconds  
count   643.000000             643.000000  
mean   1336.051322             828.895801  
min     161.000000             300.000000  
25%    1115.000000             600.000000  
50%    1160.000000             900.000000  
75%    1223.000000             900.000000  
max    9702.000000            3600.000000  
std    1150.280986             404.306098

In [329]:
# get statistics for the tier trips that start and end at a station
get_stats(night_no_delay_next_station_station, ['trip_duration_seconds', 'trip_distance_kilometers'])

column                                     trip_duration_seconds  \
rows                                                         643   
sum                                                     532980.0   
mean                                                  828.895801   
median                                                     900.0   
mode           0    600.0
Name: trip_duration_seconds, dtype:...   
max                                                       3600.0   
min                                                        300.0   
std_dev                                               404.306098   
variance                                            163463.42059   
skewness                                                2.161158   
kurtosis                                                9.721423   
percentile_25                                              600.0   
percentile_75                                              900.0   
iqr                                                        300.0   
range                                                     3300.0   
cv                                                      0.487765   
qd                                                           0.2   
cs                                                      0.005345   
ck                                                      0.024045   
cvs                                                     0.005345   
cvk                                                     0.024045   
cvcs                                                    0.005345   
cvck                                                    0.024045   
cvcv                                                    0.487765   
cvqd                                                         0.2   
cvr                                                       3.9812   
cvm                                                          1.0   
cvmed                                                   1.085782   
cvmode         0    0.723855
Name: trip_duration_seconds, dty...   

column                                  trip_distance_kilometers  
rows                                                         643  
sum                                                   990.926872  
mean                                                    1.541099  
median                                                  1.247518  
mode           0    0.98257
Name: trip_distance_kilometers, d...  
max                                                     9.640671  
min                                                      0.10092  
std_dev                                                 1.141667  
variance                                                1.303403  
skewness                                                2.210288  
kurtosis                                                8.186553  
percentile_25                                           0.825008  
percentile_75                                           1.929398  
iqr                                                      1.10439  
range                                                   9.539751  
cv                                                      0.740813  
qd                                                      0.400954  
cs                                                      1.936019  
ck                                                      7.170704  
cvs                                                     1.936019  
cvk                                                     7.170704  
cvcs                                                    1.936019  
cvck                                                    7.170704  
cvcv                                                    0.740813  
cvqd                                                    0.400954  
cvr                                                     6.190225  
cvm                                                          1.0  
cvmed                                                   0.809498  
cvmode         0

In [330]:
night_nan_delay = nan_delay[(nan_delay['scheduled_arrival_time'].dt.hour >= 22) | (nan_delay['scheduled_arrival_time'].dt.hour <= 2)]
night_nan_delay

route_id  agency_id route_short_name  route_type route_type_name  \
91             66          6               66           0            Tram   
93             66          6               66           0            Tram   
94             66          6               66           0            Tram   
98             66          6               66           0            Tram   
103            66          6               66           0            Tram   
...           ...        ...              ...         ...             ...   
2564713       686          6               N6           3             Bus   
2564721       686          6               N6           3             Bus   
2564735       686          6               N6           3             Bus   
2564742       686          6               N6           3             Bus   
2564744       686          6               N6           3             Bus   

                               agency_name  service_id  \
91       SWB Stadtwerke Bonn Verkehrs GmbH       27306   
93       SWB Stadtwerke Bonn Verkehrs GmbH       27306   
94       SWB Stadtwerke Bonn Verkehrs GmbH       27306   
98       SWB Stadtwerke Bonn Verkehrs GmbH       27306   
103      SWB Stadtwerke Bonn Verkehrs GmbH       27306   
...                                    ...         ...   
2564713  SWB Stadtwerke Bonn Verkehrs GmbH         179   
2564721  SWB Stadtwerke Bonn Verkehrs GmbH         179   
2564735  SWB Stadtwerke Bonn Verkehrs GmbH         179   
2564742  SWB Stadtwerke Bonn Verkehrs GmbH         179   
2564744  SWB Stadtwerke Bonn Verkehrs GmbH         179   

                                                   trip_id trip_headsign  \
91       660317-66-006-1788.1.11:245200-37-177_CC1FB427...   Siegburg Bf   
93       660317-66-006-1788.1.11:245200-37-177_CC1FB427...   Siegburg Bf   
94       660317-66-006-1788.1.11:245200-37-177_CC1FB427...   Siegburg Bf   
98       660317-66-006-1788.1.11:245200-37-177_CC1FB427...   Siegburg Bf   
103      660317-66-006-1788.1.11:245200-37-177_CC1FB427...   Siegburg Bf   
...                                                    ...           ...   
2564713  6860005-686-006-687.2.21:263500-50-1_C24030E9-...      Bonn Hbf   
2564721  6860005-686-006-687.2.21:263500-50-1_C24030E9-...      Bonn Hbf   
2564735  6860005-686-006-687.2.21:263500-50-1_C24030E9-...      Bonn Hbf   
2564742  6860005-686-006-687.2.21:263500-50-1_C24030E9-...      Bonn Hbf   
2564744  6860005-686-006-687.2.21:263500-50-1_C24030E9-...      Bonn Hbf   

         direction_id  ...  delay_span  arrival_delay_span weather_int  \
91                  0  ...           0                   0           0   
93                  0  ...           0                   0           0   
94                  0  ...           0                   0           0   
98                  0  ...           0                   0           0   
103                 0  ...           0                   0           0   
...               ...  ...         ...                 ...         ...   
2564713             0  ...           0                   0           1   
2564721             0  ...           0                   0           1   
2564735             0  ...           0                   0           1   
2564742             0  ...           0                   0           1   
2564744             0  ...           0                   0           1   

        time_span_arrival  time_span_int_arrival  weekend time_span  \
91                      0                      0        2         0   
93                      0                      0        2         0   
94                      0                      0        2         0   
98                      0                      0        2         0   
103                     0                      0        2         0   
...                   ...                    ...      ...       ...   
2564713                 0                      0        0         0   
2564721          

In [331]:
get_stats(night_nan_delay, ['tier_trips_count', 'tier_trips_end_at_station_count', 'nextbike_trips_count', 'nextbike_trips_end_at_station_count', 'current_temp', 'current_precipitation_volume'])

/tmp/ipykernel_2575952/41814695.py:51: RuntimeWarning: invalid value encountered in scalar divide
  qd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:55: RuntimeWarning: invalid value encountered in scalar divide
  cvqd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:51: RuntimeWarning: invalid value encountered in scalar divide
  qd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:55: RuntimeWarning: invalid value encountered in scalar divide
  cvqd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:51: RuntimeWarning: invalid value encountered in scalar divide
  qd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:55: RuntimeWarning: invalid value encountered in scalar divide
  cvqd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:51: RuntimeWarning: invalid value encountered in scalar divide
  qd = iqr / (percentile_75 + percenti

column                                        tier_trips_count  \
rows                                                     63884   
sum                                                       1012   
mean                                                  0.015841   
median                                                     0.0   
mode               0    0
Name: tier_trips_count, dtype: int64   
max                                                          5   
min                                                          0   
std_dev                                               0.152412   
variance                                              0.023229   
skewness                                              13.18146   
kurtosis                                            242.465644   
percentile_25                                              0.0   
percentile_75                                              0.0   
iqr                                                        0.0   
range                                                        5   
cv                                                    9.621246   
qd                                                         NaN   
cs                                                   86.485601   
ck                                                 1590.854615   
cvs                                                  86.485601   
cvk                                                1590.854615   
cvcs                                                 86.485601   
cvck                                               1590.854615   
cvcv                                                  9.621246   
cvqd                                                       NaN   
cvr                                                 315.632411   
cvm                                                        1.0   
cvmed                                                      0.0   
cvmode         0    0.0
Name: tier_trips_count, dtype: float64   

column                           tier_trips_end_at_station_count  \
rows                                                       63884   
sum                                                          845   
mean                                                    0.013227   
median                                                       0.0   
mode           0    0
Name: tier_trips_end_at_station_count, ...   
max                                                            5   
min                                                            0   
std_dev                                                 0.136703   
variance                                                0.018688   
skewness                                               13.637034   
kurtosis                                              250.096789   
percentile_25                                                0.0   
percentile_75                                                0.0   
iqr                                                          0.0   
range                                                          5   
cv                                                     10.335054   
qd                                                           NaN   
cs                                                     99.756817   
ck                                                   1829.493109   
cvs                                                    99.756817   
cvk                                                  1829.493109   
cvcs                                                   99.756817   
cvck                                                 1829.493109   
cvcv                                                   10.335054   
cvqd                                                         NaN   
cvr                                                   378.011834   
cvm                                                          1.0   
cvmed                                                        0.0   
cvmode         0    0.0
Name: tier_trips_end_at

In [332]:
night_nan_delay_tier = check_micromobility_datasets('tier', night_nan_delay)

In [333]:
night_nan_delay_tier.describe()

tier_trips_id          tier_trips_start_time  \
count   6.600000e+02                            660   
mean    8.010155e+08  2023-07-15 19:22:33.181818368   
min     7.822653e+08            2023-07-01 01:25:00   
25%     7.823707e+08            2023-07-07 23:10:00   
50%     8.086423e+08            2023-07-14 22:37:30   
75%     8.087683e+08            2023-07-23 22:21:15   
max     8.323115e+08            2023-07-31 23:15:00   
std     1.837476e+07                            NaN   

                 tier_trips_end_time              trip_duration  \
count                            660                        660   
mean   2023-07-15 19:37:51.454545408  0 days 00:15:18.272727272   
min              2023-07-01 01:40:00            0 days 00:05:00   
25%              2023-07-07 23:20:00            0 days 00:10:00   
50%              2023-07-14 23:00:00            0 days 00:15:00   
75%              2023-07-23 23:11:15            0 days 00:20:00   
max              2023-07-31 23:30:00            0 days 01:45:00   
std                              NaN  0 days 00:09:50.361673705   

       trip_distance_kilometers  trip_distance_meters  start_stop_id  \
count                660.000000            660.000000     544.000000   
mean                   2.210355           2210.354966    1083.740809   
min                    0.101267            101.267318      43.000000   
25%                    0.992140            992.140467     687.000000   
50%                    1.841834           1841.833745    1102.000000   
75%                    2.963518           2963.518194    1174.500000   
max                   11.059508          11059.507664    9701.000000   
std                    1.675474           1675.473990     837.074367   

       end_stop_id  trip_duration_seconds  
count   354.000000             660.000000  
mean   1611.872881             918.272727  
min     161.000000             300.000000  
25%    1115.000000             600.000000  
50%    1178.500000             900.000000  
75%    1485.500000            1200.000000  
max    9478.000000            6300.000000  
std    1626.602188             590.361674

In [334]:
get_stats(night_nan_delay_tier, ['trip_duration_seconds', 'trip_distance_kilometers'])

column                                     trip_duration_seconds  \
rows                                                         660   
sum                                                     606060.0   
mean                                                  918.272727   
median                                                     900.0   
mode           0    600.0
Name: trip_duration_seconds, dtype:...   
max                                                       6300.0   
min                                                        300.0   
std_dev                                               590.361674   
variance                                            348526.90578   
skewness                                                3.844443   
kurtosis                                               25.292501   
percentile_25                                              600.0   
percentile_75                                             1200.0   
iqr                                                        600.0   
range                                                     6000.0   
cv                                                      0.642905   
qd                                                      0.333333   
cs                                                      0.006512   
ck                                                      0.042842   
cvs                                                     0.006512   
cvk                                                     0.042842   
cvcs                                                    0.006512   
cvck                                                    0.042842   
cvcv                                                    0.642905   
cvqd                                                    0.333333   
cvr                                                     6.534007   
cvm                                                          1.0   
cvmed                                                   0.980101   
cvmode         0    0.653401
Name: trip_duration_seconds, dty...   

column                                  trip_distance_kilometers  
rows                                                         660  
sum                                                  1458.834277  
mean                                                    2.210355  
median                                                  1.841834  
mode           0       0.101267
1       0.105063
2       0.10...  
max                                                    11.059508  
min                                                     0.101267  
std_dev                                                 1.675474  
variance                                                2.807213  
skewness                                                1.597203  
kurtosis                                                3.664222  
percentile_25                                            0.99214  
percentile_75                                           2.963518  
iqr                                                     1.971378  
range                                                   10.95824  
cv                                                      0.758011  
qd                                                      0.498369  
cs                                                      0.953284  
ck                                                      2.186976  
cvs                                                     0.953284  
cvk                                                     2.186976  
cvcs                                                    0.953284  
cvck                                                    2.186976  
cvcv                                                    0.758011  
cvqd                                                    0.498369  
cvr                                                     4.957684  
cvm                                                          1.0  
cvmed                                                   0.833275  
cvmode         0

In [335]:
# get entries where trips start and end at station
night_nan_delay_tier_station_station = night_nan_delay_tier[night_nan_delay_tier['end_stop_id'].notna() & night_nan_delay_tier['start_stop_id'].notna()]
night_nan_delay_tier_station_station

tier_trips_id tier_trips_start_time tier_trips_end_time vehicle type  \
3190399      782373031   2023-07-01 01:25:00 2023-07-01 01:40:00    e-scooter   
3209527      782391260   2023-07-01 01:45:00 2023-07-01 01:50:00    e-scooter   
3210269      782391943   2023-07-01 01:45:00 2023-07-01 01:50:00    e-scooter   
3201996      782383745   2023-07-01 02:20:00 2023-07-01 02:25:00    e-scooter   
3276897      782452649   2023-07-01 02:20:00 2023-07-01 02:25:00    e-scooter   
...                ...                   ...                 ...          ...   
3422524      832205249   2023-07-31 22:25:00 2023-07-31 22:45:00    e-scooter   
3485596      832265817   2023-07-31 22:25:00 2023-07-31 22:45:00    e-scooter   
3518645      832297525   2023-07-31 22:55:00 2023-07-31 23:00:00    e-scooter   
3420883      832203680   2023-07-31 23:00:00 2023-07-31 23:05:00    e-scooter   
3421744      832204504   2023-07-31 23:15:00 2023-07-31 23:25:00    e-scooter   

          trip_duration  trip_distance_kilometers  trip_distance_meters  \
3190399 0 days 00:15:00                  1.055901           1055.901028   
3209527 0 days 00:05:00                  0.670973            670.973151   
3210269 0 days 00:05:00                  0.838693            838.692953   
3201996 0 days 00:05:00                  0.567479            567.479089   
3276897 0 days 00:05:00                  0.589011            589.011497   
...                 ...                       ...                   ...   
3422524 0 days 00:20:00                  1.197806           1197.806121   
3485596 0 days 00:20:00                  1.171579           1171.578745   
3518645 0 days 00:05:00                  0.704362            704.361980   
3420883 0 days 00:05:00                  0.369227            369.226899   
3421744 0 days 00:10:00                  1.002491           1002.491082   

         start_stop_id                            start_stop_name  \
3190399          686.0                     Bonn Universität/Markt   
3209527         1115.0  Bonn Bertha-Von-Suttner-Pl./Beethovenhaus   
3210269         1115.0  Bonn Bertha-Von-Suttner-Pl./Beethovenhaus   
3201996          687.0                                   Bonn Hbf   
3276897          687.0                                   Bonn Hbf   
...                ...                                        ...   
3422524          686.0                     Bonn Universität/Markt   
3485596          686.0                     Bonn Universität/Markt   
3518645         1115.0  Bonn Bertha-Von-Suttner-Pl./Beethovenhaus   
3420883         1115.0  Bonn Bertha-Von-Suttner-Pl./Beethovenhaus   
3421744         1504.0                              Bonn Beuel Bf   

                                         start_buffer_zone  end_stop_id  \
3190399  801621     POLYGON ((7.157885983913106 50.7227...       1110.0   
3209527  801621     POLYGON ((7.157885983913106 50.7227...        687.0   
3210269  801621     POLYGON ((7.157885983913106 50.7227...        687.0   
3201996  801621     POLYGON ((7.157885983913106 50.7227...       1103.0   
3276897  801621     POLYGON ((7.157885983913106 50.7227...       1103.0   
...                                                    ...          ...   
3422524  801621     POLYGON ((7.157885983913106 50.7227...       1153.0   
3485596  801621     POLYGON ((7.157885983913106 50.7227...       1153.0   
3518645  801621     POLYGON ((7.157885983913106 50.7227...       1161.0   
3420883  801621     POLYGON ((7.157885983913106 50.7227...       1115.0   
3421744  801621     POLYGON ((7.157885983913106 50.7227...       1126.0   

                                     end_stop_name  \
3190399                         Bonn Wilhelmsplatz   
3209527                                   Bonn Hbf   
3210269                                   Bonn Hbf   
3201996                                 Bonn Markt   
3276897                                 Bonn Markt   
...                                            ...   
3422524                    

In [336]:
night_nan_delay_tier_station_station.describe()

tier_trips_id          tier_trips_start_time  \
count   3.310000e+02                            331   
mean    8.021715e+08  2023-07-16 14:58:03.081571072   
min     7.822653e+08            2023-07-01 01:25:00   
25%     7.823723e+08            2023-07-08 01:07:30   
50%     8.086652e+08            2023-07-15 22:20:00   
75%     8.087832e+08            2023-07-24 23:45:00   
max     8.323115e+08            2023-07-31 23:15:00   
std     1.823943e+07                            NaN   

                 tier_trips_end_time              trip_duration  \
count                            331                        331   
mean   2023-07-16 15:12:43.323262976  0 days 00:14:40.241691842   
min              2023-07-01 01:40:00            0 days 00:05:00   
25%              2023-07-08 01:20:00            0 days 00:10:00   
50%              2023-07-15 22:50:00            0 days 00:15:00   
75%              2023-07-24 23:57:30            0 days 00:15:00   
max              2023-07-31 23:25:00            0 days 01:35:00   
std                              NaN  0 days 00:09:05.478329610   

       trip_distance_kilometers  trip_distance_meters  start_stop_id  \
count                331.000000            331.000000     331.000000   
mean                   1.895242           1895.241503    1047.371601   
min                    0.106863            106.863116      43.000000   
25%                    0.869809            869.809404     687.000000   
50%                    1.626380           1626.379881    1102.000000   
75%                    2.705733           2705.733107    1153.000000   
max                    6.761793           6761.793236    8471.000000   
std                    1.343772           1343.771980     553.737136   

       end_stop_id  trip_duration_seconds  
count   331.000000             331.000000  
mean   1659.003021             880.241692  
min     684.000000             300.000000  
25%    1126.000000             600.000000  
50%    1184.000000             900.000000  
75%    1500.000000             900.000000  
max    9478.000000            5700.000000  
std    1667.134996             545.478330

In [337]:
# get statistics for the tier trips that start and end at a station
get_stats(night_nan_delay_tier_station_station, ['trip_duration_seconds', 'trip_distance_kilometers'])

column                                     trip_duration_seconds  \
rows                                                         331   
sum                                                     291360.0   
mean                                                  880.241692   
median                                                     900.0   
mode           0    600.0
Name: trip_duration_seconds, dtype:...   
max                                                       5700.0   
min                                                        300.0   
std_dev                                                545.47833   
variance                                           297546.608075   
skewness                                                3.722788   
kurtosis                                               23.814927   
percentile_25                                              600.0   
percentile_75                                              900.0   
iqr                                                        300.0   
range                                                     5400.0   
cv                                                      0.619692   
qd                                                           0.2   
cs                                                      0.006825   
ck                                                      0.043659   
cvs                                                     0.006825   
cvk                                                     0.043659   
cvcs                                                    0.006825   
cvck                                                    0.043659   
cvcv                                                    0.619692   
cvqd                                                         0.2   
cvr                                                     6.134679   
cvm                                                          1.0   
cvmed                                                   1.022446   
cvmode         0    0.681631
Name: trip_duration_seconds, dty...   

column                                  trip_distance_kilometers  
rows                                                         331  
sum                                                   627.324937  
mean                                                    1.895242  
median                                                   1.62638  
mode           0      0.106863
1      0.109334
2      0.11604...  
max                                                     6.761793  
min                                                     0.106863  
std_dev                                                 1.343772  
variance                                                1.805723  
skewness                                                0.973443  
kurtosis                                                0.727252  
percentile_25                                           0.869809  
percentile_75                                           2.705733  
iqr                                                     1.835924  
range                                                    6.65493  
cv                                                      0.709024  
qd                                                      0.513467  
cs                                                      0.724411  
ck                                                      0.541202  
cvs                                                     0.724411  
cvk                                                     0.541202  
cvcs                                                    0.724411  
cvck                                                    0.541202  
cvcv                                                    0.709024  
cvqd                                                    0.513467  
cvr                                                     3.511389  
cvm                                                          1.0  
cvmed                                                   0.858139  
cvmode         0

In [338]:
night_nan_delay_next = check_micromobility_datasets('next', evening_nan_delay)

In [339]:
night_nan_delay_next.describe()

nextbike_trips_id      nextbike_trips_start_time  \
count       1.555000e+03                           1555   
mean        3.793712e+07  2023-07-15 15:02:59.922829824   
min         3.771653e+07            2023-07-01 20:01:00   
25%         3.782244e+07            2023-07-07 21:01:00   
50%         3.793590e+07            2023-07-14 20:01:00   
75%         3.804858e+07            2023-07-22 20:51:00   
max         3.817128e+07            2023-07-31 22:01:00   
std         1.301384e+05                            NaN   

             nextbike_trips_end_time              trip_duration  \
count                           1555                       1555   
mean   2023-07-15 15:18:22.881028864  0 days 00:15:22.958199356   
min              2023-07-01 20:11:00            0 days 00:05:00   
25%              2023-07-07 21:16:00            0 days 00:10:00   
50%              2023-07-14 20:11:00            0 days 00:15:00   
75%              2023-07-22 21:11:00            0 days 00:20:00   
max              2023-07-31 22:26:00            0 days 01:50:00   
std                              NaN  0 days 00:08:38.118062877   

       trip_distance_kilometers  trip_distance_meters  start_stop_id  \
count               1555.000000           1555.000000    1277.000000   
mean                   1.871948           1871.948110    1146.364918   
min                    0.100866            100.866433      43.000000   
25%                    0.922408            922.407833     687.000000   
50%                    1.519255           1519.255105    1112.000000   
75%                    2.399824           2399.823501    1190.000000   
max                    9.640671           9640.671235    9702.000000   
std                    1.415567           1415.567226     911.078831   

       end_stop_id  trip_duration_seconds  
count   875.000000            1555.000000  
mean   1340.654857             922.958199  
min      43.000000             300.000000  
25%    1111.000000             600.000000  
50%    1160.000000             900.000000  
75%    1224.000000            1200.000000  
max    9780.000000            6600.000000  
std    1243.646601             518.118063

In [340]:
get_stats(night_nan_delay_next, ['trip_duration_seconds', 'trip_distance_kilometers'])

column                                     trip_duration_seconds  \
rows                                                        1555   
sum                                                    1435200.0   
mean                                                  922.958199   
median                                                     900.0   
mode           0    600.0
Name: trip_duration_seconds, dtype:...   
max                                                       6600.0   
min                                                        300.0   
std_dev                                               518.118063   
variance                                            268446.32708   
skewness                                                3.257454   
kurtosis                                               23.426094   
percentile_25                                              600.0   
percentile_75                                             1200.0   
iqr                                                        600.0   
range                                                     6300.0   
cv                                                      0.561367   
qd                                                      0.333333   
cs                                                      0.006287   
ck                                                      0.045214   
cvs                                                     0.006287   
cvk                                                     0.045214   
cvcs                                                    0.006287   
cvck                                                    0.045214   
cvcv                                                    0.561367   
cvqd                                                    0.333333   
cvr                                                     6.825878   
cvm                                                          1.0   
cvmed                                                   0.975125   
cvmode         0    0.650084
Name: trip_duration_seconds, dty...   

column                                  trip_distance_kilometers  
rows                                                        1555  
sum                                                  2910.879311  
mean                                                    1.871948  
median                                                  1.519255  
mode           0    0.982570
1    2.199943
Name: trip_distanc...  
max                                                     9.640671  
min                                                     0.100866  
std_dev                                                 1.415567  
variance                                                2.003831  
skewness                                                 1.72309  
kurtosis                                                3.858902  
percentile_25                                           0.922408  
percentile_75                                           2.399824  
iqr                                                     1.477416  
range                                                   9.539805  
cv                                                        0.7562  
qd                                                      0.444706  
cs                                                      1.217243  
ck                                                      2.726046  
cvs                                                     1.217243  
cvk                                                     2.726046  
cvcs                                                    1.217243  
cvck                                                    2.726046  
cvcv                                                      0.7562  
cvqd                                                    0.444706  
cvr                                                     5.096191  
cvm                                                          1.0  
cvmed                                                    0.81159  
cvmode         0

In [341]:
# get entries where trips start and end at station
night_nan_delay_next_station_station = night_nan_delay_next[night_nan_delay_next['end_stop_id'].notna() & night_nan_delay_next['start_stop_id'].notna()]
night_nan_delay_next_station_station

nextbike_trips_id nextbike_trips_start_time nextbike_trips_end_time  \
1245075           37816421       2023-07-01 20:01:00     2023-07-01 20:11:00   
1318686           37853724       2023-07-01 20:06:00     2023-07-01 20:16:00   
1515605           38105105       2023-07-01 20:06:00     2023-07-01 20:46:00   
1218963           37716529       2023-07-01 20:16:00     2023-07-01 20:41:00   
1422829           38000439       2023-07-01 20:21:00     2023-07-01 20:41:00   
...                    ...                       ...                     ...   
1392716           37984594       2023-07-31 21:31:00     2023-07-31 21:46:00   
1252775           37820583       2023-07-31 21:31:00     2023-07-31 21:41:00   
1223579           37720859       2023-07-31 21:46:00     2023-07-31 21:56:00   
1329312           37892654       2023-07-31 22:01:00     2023-07-31 22:16:00   
1335610           37895414       2023-07-31 22:01:00     2023-07-31 22:16:00   

         nextbike_trips_start_at_station  nextbike_trips_end_at_station  \
1245075                            False                          False   
1318686                            False                          False   
1515605                            False                          False   
1218963                            False                          False   
1422829                            False                          False   
...                                  ...                            ...   
1392716                            False                          False   
1252775                            False                          False   
1223579                            False                          False   
1329312                             True                          False   
1335610                             True                          False   

        vehicle type   trip_duration  trip_distance_kilometers  \
1245075         bike 0 days 00:10:00                  3.114978   
1318686         bike 0 days 00:10:00                  0.100866   
1515605         bike 0 days 00:40:00                  7.408574   
1218963         bike 0 days 00:25:00                  2.825435   
1422829         bike 0 days 00:20:00                  2.699145   
...              ...             ...                       ...   
1392716         bike 0 days 00:15:00                  2.389327   
1252775         bike 0 days 00:10:00                  0.935837   
1223579         bike 0 days 00:10:00                  1.151484   
1329312         bike 0 days 00:15:00                  1.645817   
1335610         bike 0 days 00:15:00                  1.831696   

         trip_distance_meters  \
1245075           3114.978233   
1318686            100.866433   
1515605           7408.574406   
1218963           2825.434827   
1422829           2699.145397   
...                       ...   
1392716           2389.326515   
1252775            935.836836   
1223579           1151.483630   
1329312           1645.816542   
1335610           1831.695734   

                                            start_location  \
1245075  b'\x01\x01\x00\x00\x00R\x0f\xd1\xe8\x0eb\x1c@\...   
1318686  b'\x01\x01\x00\x00\x00\x85\xcf\xd6\xc1\xc1\x8e...   
1515605  b'\x01\x01\x00\x00\x00\xa7Z\x0b\xb3\xd0\x8e\x1...   
1218963  b'\x01\x01\x00\x00\x00\xf6\xed$"\xfc[\x1c@\xfb...   
1422829  b'\x01\x01\x00\x00\x00\xffA$C\x8e]\x1c@4\xbf\x...   
...                                                    ...   
1392716  b'\x01\x01\x00\x00\x00\xac\xc9SV\xd3e\x1c@+MJA...   
1252775  b'\x01\x01\x00\x00\x00I\xa2\x97Q,g\x1c@\x1e\xc...   
1223579  b'\x01\x01\x00\x00\x00\xa7 ?\x1b\xb9~\x1c@\x9a...   
1329312  b'\x01\x01\x00\x00\x00|H\xf8\xde\xdf`\x1c@/\xe...   
1335610  b'\x01\x01\x00\x00\x00\xeb;\xbf(A/\x1c@i\xfd-\...   

                                              end_location  start_stop_id  \
1245075  b'\x01\x01\x00\x00\x00]j\x84~\xa6~\x1c@E+\xf7\...         1102.0   
1318686  b'\x01\x01\x00\x00\x00\nj\xf8\x16\xd6\x8d\x1c@...

In [342]:
night_nan_delay_next_station_station.describe()

nextbike_trips_id      nextbike_trips_start_time  \
count       7.610000e+02                            761   
mean        3.794043e+07  2023-07-15 17:30:12.851510784   
min         3.771653e+07            2023-07-01 20:01:00   
25%         3.782492e+07            2023-07-07 21:06:00   
50%         3.793888e+07            2023-07-14 20:26:00   
75%         3.805421e+07            2023-07-22 20:16:00   
max         3.817128e+07            2023-07-31 22:01:00   
std         1.306728e+05                            NaN   

             nextbike_trips_end_time              trip_duration  \
count                            761                        761   
mean   2023-07-15 17:44:19.237844992  0 days 00:14:06.386333771   
min              2023-07-01 20:11:00            0 days 00:05:00   
25%              2023-07-07 21:21:00            0 days 00:10:00   
50%              2023-07-14 20:46:00            0 days 00:15:00   
75%              2023-07-22 20:31:00            0 days 00:15:00   
max              2023-07-31 22:16:00            0 days 01:50:00   
std                              NaN  0 days 00:08:16.637857071   

       trip_distance_kilometers  trip_distance_meters  start_stop_id  \
count                761.000000            761.000000     761.000000   
mean                   1.562615           1562.615472    1185.822602   
min                    0.100866            100.866433      43.000000   
25%                    0.791171            791.171279     688.000000   
50%                    1.254460           1254.459733    1115.000000   
75%                    1.932509           1932.508700    1182.000000   
max                    9.640671           9640.671235    9702.000000   
std                    1.219393           1219.392681     990.946906   

       end_stop_id  trip_duration_seconds  
count   761.000000             761.000000  
mean   1361.869908             846.386334  
min     161.000000             300.000000  
25%    1112.000000             600.000000  
50%    1160.000000             900.000000  
75%    1223.000000             900.000000  
max    9780.000000            6600.000000  
std    1270.535926             496.637857

In [343]:
# get statistics for the tier trips that start and end at a station
get_stats(night_nan_delay_next_station_station, ['trip_duration_seconds', 'trip_distance_kilometers'])

column                                     trip_duration_seconds  \
rows                                                         761   
sum                                                     644100.0   
mean                                                  846.386334   
median                                                     900.0   
mode           0    600.0
Name: trip_duration_seconds, dtype:...   
max                                                       6600.0   
min                                                        300.0   
std_dev                                               496.637857   
variance                                           246649.161076   
skewness                                                4.663434   
kurtosis                                               43.950066   
percentile_25                                              600.0   
percentile_75                                              900.0   
iqr                                                        300.0   
range                                                     6300.0   
cv                                                      0.586774   
qd                                                           0.2   
cs                                                       0.00939   
ck                                                      0.088495   
cvs                                                      0.00939   
cvk                                                     0.088495   
cvcs                                                     0.00939   
cvck                                                    0.088495   
cvcv                                                    0.586774   
cvqd                                                         0.2   
cvr                                                     7.443409   
cvm                                                          1.0   
cvmed                                                   1.063344   
cvmode         0    0.708896
Name: trip_duration_seconds, dty...   

column                                  trip_distance_kilometers  
rows                                                         761  
sum                                                  1189.150374  
mean                                                    1.562615  
median                                                   1.25446  
mode           0    0.98257
Name: trip_distance_kilometers, d...  
max                                                     9.640671  
min                                                     0.100866  
std_dev                                                 1.219393  
variance                                                1.486919  
skewness                                                2.197744  
kurtosis                                                7.343652  
percentile_25                                           0.791171  
percentile_75                                           1.932509  
iqr                                                     1.141337  
range                                                   9.539805  
cv                                                      0.780354  
qd                                                      0.419042  
cs                                                      1.802327  
ck                                                      6.022385  
cvs                                                     1.802327  
cvk                                                     6.022385  
cvcs                                                    1.802327  
cvck                                                    6.022385  
cvcv                                                    0.780354  
cvqd                                                    0.419042  
cvr                                                     6.105024  
cvm                                                          1.0  
cvmed                                                   0.802795  
cvmode         0

In [344]:
night_delay.describe()

route_id     agency_id    route_type    service_id  direction_id  \
count  95607.000000  95607.000000  95607.000000  95607.000000  95607.000000   
mean     569.783677      6.005282      2.733597   2389.985221      0.437144   
min       18.000000      1.000000      0.000000      3.000000      0.000000   
25%      602.000000      6.000000      3.000000     43.000000      0.000000   
50%      608.000000      6.000000      3.000000     43.000000      0.000000   
75%      612.000000      6.000000      3.000000    151.000000      1.000000   
max      690.000000      8.000000      3.000000  27318.000000      1.000000   
std      163.243022      0.104414      0.853373   7565.950599      0.496036   

           shape_id       stop_id            actual_arrival_time  \
count  95607.000000  95607.000000                          93672   
mean    3896.012143   2320.269133  2023-07-17 03:04:29.344916224   
min      118.000000    371.000000            2023-07-01 01:24:50   
25%     1945.000000   1210.000000            2023-07-09 00:25:30   
50%     2898.000000   1431.000000            2023-07-17 22:54:15   
75%     5633.000000   1687.000000            2023-07-24 23:15:00   
max    10396.000000   9780.000000            2023-08-01 03:15:45   
std     2809.202122   2415.607424                            NaN   

               actual_departure_time  vrs_timestamp  ...  \
count                          95607   95607.000000  ...   
mean   2023-07-17 03:18:57.938331136  216472.522305  ...   
min              2023-07-01 01:25:10     804.000000  ...   
25%              2023-07-09 00:23:45  211804.000000  ...   
50%              2023-07-17 22:55:15  215305.000000  ...   
75%              2023-07-24 23:19:15  221806.000000  ...   
max              2023-08-01 03:16:00  235807.000000  ...   
std                              NaN   17271.076180  ...   

       departure_delay_float actual_arrival_time_float  \
count           95607.000000              95607.000000   
mean                1.344429             171057.656416   
min                 0.000000                  0.000000   
25%                 0.250000              25315.000000   
50%                 0.500000             223730.000000   
75%                 0.750000             231430.000000   
max                51.500000             235945.000000   
std                 5.235768              95477.075924   

      actual_departure_time_float arrival_delay_span   weather_int  \
count                95607.000000            95607.0  95607.000000   
mean                174153.268589                0.0      0.156191   
min                      0.000000                0.0      0.000000   
25%                 220030.000000                0.0      0.000000   
50%                 223915.000000                0.0      0.000000   
75%                 231545.000000                0.0      0.000000   
max                 235950.000000                0.0      2.000000   
std                  93510.374855                0.0      0.394598   

       time_span_int_arrival       weekend  time_span_int  delay_category  \
count           95607.000000  95607.000000   95607.000000    95607.000000   
mean                0.028450      0.856329       0.028617        0.655768   
min                 0.000000      0.000000       0.000000       -1.000000   
25%                 0.000000      0.000000       0.000000        0.000000   
50%                 0.000000      0.000000       0.000000        1.000000   
75%                 0.000000      2.000000       0.000000        1.000000   
max                 8.000000      3.000000       8.000000        1.000000   
std                 0.476226      1.124596       0.477620        0.515963   

       cancelled_trip  
count         95607.0  
mean              0.0  
min               0.0  
25%               0.0  
50%               0.0  
75%               0.0  
max               0.0  
std               0.0  

[8 rows x 38 columns]

In [345]:
night_no_delay.describe()

route_id     agency_id    route_type    service_id  direction_id  \
count  60743.000000  60743.000000  60743.000000  60743.000000  60743.000000   
mean     539.706435      6.902392      2.516586   5698.631727      0.447113   
min       16.000000      1.000000      0.000000      3.000000      0.000000   
25%      550.000000      6.000000      3.000000     43.000000      0.000000   
50%      606.000000      6.000000      3.000000     64.000000      0.000000   
75%      612.000000      6.000000      3.000000    179.000000      1.000000   
max      857.000000     12.000000      3.000000  29130.000000      1.000000   
std      232.677613      2.057855      1.102983  10982.432309      0.497199   

           shape_id       stop_id            actual_arrival_time  \
count  60743.000000  60743.000000                          45341   
mean    4426.226512   2184.661064  2023-07-16 20:28:33.687479552   
min      118.000000     43.000000            2023-07-01 00:33:00   
25%     2021.000000   1176.000000            2023-07-08 22:54:00   
50%     3948.000000   1454.000000            2023-07-17 21:59:40   
75%     7302.000000   1710.000000            2023-07-24 22:41:40   
max    10396.000000   9778.000000            2023-08-01 02:58:45   
std     2892.425477   2306.737286                            NaN   

               actual_departure_time  vrs_timestamp  ...  \
count                          60743   60743.000000  ...   
mean   2023-07-16 21:51:33.924468736  215942.121479  ...   
min              2023-07-01 00:32:00     308.000000  ...   
25%              2023-07-08 23:15:00  211804.000000  ...   
50%              2023-07-17 02:42:00  215304.000000  ...   
75%              2023-07-24 22:43:00  221808.000000  ...   
max              2023-08-01 02:59:00  235807.000000  ...   
std                              NaN   17858.483417  ...   

       departure_delay_float actual_arrival_time_float  \
count           60743.000000              60743.000000   
mean                0.047644             133364.154948   
min                 0.000000                  0.000000   
25%                 0.000000                  0.000000   
50%                 0.000000             221445.000000   
75%                 0.000000             230445.000000   
max                46.750000             235945.000000   
std                 0.915175             110681.530272   

      actual_departure_time_float arrival_delay_span   weather_int  \
count                60743.000000            60743.0  60743.000000   
mean                177354.498362                0.0      0.162784   
min                      0.000000                0.0      0.000000   
25%                 220300.000000                0.0      0.000000   
50%                 224100.000000                0.0      0.000000   
75%                 231700.000000                0.0      0.000000   
max                 235950.000000                0.0      2.000000   
std                  92287.204460                0.0      0.400569   

       time_span_int_arrival       weekend  time_span_int  delay_category  \
count           60743.000000  60743.000000   60743.000000    60743.000000   
mean                0.028645      0.918526       0.000263       -0.247782   
min                 0.000000      0.000000       0.000000       -1.000000   
25%                 0.000000      0.000000       0.000000       -1.000000   
50%                 0.000000      0.000000       0.000000        0.000000   
75%                 0.000000      2.000000       0.000000        0.000000   
max                 6.000000      3.000000       8.000000        1.000000   
std                 0.413587      1.152835       0.045904        0.444911   

       cancelled_trip  
count         60743.0  
mean              0.0  
min               0.0  
25%               0.0  
50%               0.0  
75%               0.0  
max               0.0  
std               0.0  

[8 rows x 38 columns]

In [346]:
night_nan_delay.describe()

route_id     agency_id    route_type    service_id  direction_id  \
count  63884.000000  63884.000000  63884.000000  63884.000000  63884.000000   
mean     551.229322      6.120155      2.639440   3293.263791      0.417068   
min       16.000000      1.000000      0.000000      3.000000      0.000000   
25%      602.000000      6.000000      3.000000     43.000000      0.000000   
50%      608.000000      6.000000      3.000000     43.000000      0.000000   
75%      612.000000      6.000000      3.000000    151.000000      1.000000   
max      857.000000     12.000000      3.000000  29132.000000      1.000000   
std      190.083558      0.795591      0.975546   8727.106859      0.493078   

           shape_id       stop_id actual_arrival_time actual_departure_time  \
count  63884.000000  63884.000000                   0                     0   
mean    4258.056790   2201.324103                 NaT                   NaT   
min      118.000000     43.000000                 NaT                   NaT   
25%     2021.000000   1203.000000                 NaT                   NaT   
50%     3858.000000   1442.000000                 NaT                   NaT   
75%     6327.000000   1670.000000                 NaT                   NaT   
max    10396.000000   9780.000000                 NaT                   NaT   
std     2871.770645   2275.606444                 NaN                   NaN   

       vrs_timestamp  ...  departure_delay_float actual_arrival_time_float  \
count   63884.000000  ...                    0.0                   63884.0   
mean   215642.368887  ...                    NaN                       0.0   
min      1305.000000  ...                    NaN                       0.0   
25%    210807.000000  ...                    NaN                       0.0   
50%    215305.000000  ...                    NaN                       0.0   
75%    222804.000000  ...                    NaN                       0.0   
max    235807.000000  ...                    NaN                       0.0   
std     20170.162861  ...                    NaN                       0.0   

      actual_departure_time_float arrival_delay_span   weather_int  \
count                     63884.0            63884.0  63884.000000   
mean                          0.0                0.0      0.176695   
min                           0.0                0.0      0.000000   
25%                           0.0                0.0      0.000000   
50%                           0.0                0.0      0.000000   
75%                           0.0                0.0      0.000000   
max                           0.0                0.0      2.000000   
std                           0.0                0.0      0.407678   

       time_span_int_arrival       weekend  time_span_int  delay_category  \
count                63884.0  63884.000000        63884.0         63884.0   
mean                     0.0      0.928448            0.0            -1.0   
min                      0.0      0.000000            0.0            -1.0   
25%                      0.0      0.000000            0.0            -1.0   
50%                      0.0      0.000000            0.0            -1.0   
75%                      0.0      2.000000            0.0            -1.0   
max                      0.0      3.000000            0.0            -1.0   
std                      0.0      1.139530            0.0             0.0   

       cancelled_trip  
count         63884.0  
mean              1.0  
min               1.0  
25%               1.0  
50%               1.0  
75%               1.0  
max               1.0  
std               0.0  

[8 rows x 38 columns]

#### Early Morning

In [347]:
early_morning_delay = delay[(delay['scheduled_arrival_time'].dt.hour > 2) & (delay['scheduled_arrival_time'].dt.hour < 6)]
early_morning_delay

route_id  agency_id route_short_name  route_type route_type_name  \
16            551          8              551           3             Bus   
17            551          8              551           3             Bus   
18            551          8              551           3             Bus   
19            551          8              551           3             Bus   
20            551          8              551           3             Bus   
...           ...        ...              ...         ...             ...   
2564839       689          6               N9           3             Bus   
2564841       689          6               N9           3             Bus   
2564843       688          6               N8           3             Bus   
2564847       688          6               N8           3             Bus   
2564851       688          6               N8           3             Bus   

                                      agency_name  service_id  \
16       RSVG Rhein-Sieg-Verkehrsgesellschaft mbH         125   
17       RSVG Rhein-Sieg-Verkehrsgesellschaft mbH         125   
18       RSVG Rhein-Sieg-Verkehrsgesellschaft mbH         125   
19       RSVG Rhein-Sieg-Verkehrsgesellschaft mbH         125   
20       RSVG Rhein-Sieg-Verkehrsgesellschaft mbH         125   
...                                           ...         ...   
2564839         SWB Stadtwerke Bonn Verkehrs GmbH          43   
2564841         SWB Stadtwerke Bonn Verkehrs GmbH          43   
2564843         SWB Stadtwerke Bonn Verkehrs GmbH         179   
2564847         SWB Stadtwerke Bonn Verkehrs GmbH         179   
2564851         SWB Stadtwerke Bonn Verkehrs GmbH         179   

                                                   trip_id trip_headsign  \
16       254-551-008-2071.2.22:023200-34-157_33C7EAED-7...      Bonn Hbf   
17       254-551-008-2071.2.22:023200-34-157_33C7EAED-7...      Bonn Hbf   
18       254-551-008-2071.2.22:023200-34-157_33C7EAED-7...      Bonn Hbf   
19       254-551-008-2071.2.22:023200-34-157_33C7EAED-7...      Bonn Hbf   
20       254-551-008-2071.2.22:023200-34-157_33C7EAED-7...      Bonn Hbf   
...                                                    ...           ...   
2564839  6890005-689-006-687.2.34:263500-53-1_2AFE8F0F-...      Bonn Hbf   
2564841  6890005-689-006-687.2.34:263500-53-1_2AFE8F0F-...      Bonn Hbf   
2564843  6880005-688-006-687.2.32:263500-36-1_5350170A-...      Bonn Hbf   
2564847  6880005-688-006-687.2.32:263500-36-1_5350170A-...      Bonn Hbf   
2564851  6880005-688-006-687.2.32:263500-36-1_5350170A-...      Bonn Hbf   

         direction_id  ...  delay_span  arrival_delay_span weather_int  \
16                  1  ...           0                   0           0   
17                  1  ...           0                   0           0   
18                  1  ...           0                   0           0   
19                  1  ...           0                   0           0   
20                  1  ...           0                   0           0   
...               ...  ...         ...                 ...         ...   
2564839             0  ...         0-5                   0           1   
2564841             0  ...         0-5                   0           1   
2564843             0  ...         0-5                   0           1   
2564847             0  ...         0-5                   0           1   
2564851             0  ...         0-5                   0           1   

        time_span_arrival  time_span_int_arrival  weekend      time_span  \
16                      0                      0        1  early morning   
17                      0                      0        1  early morning   
18                      0                      0        1  early morning   
19                      0                      0        1  early morning   
20                      0                      0        1  early morning   
...                   ...                    

In [348]:
get_stats(early_morning_delay, ['tier_trips_count', 'tier_trips_end_at_station_count', 'nextbike_trips_count', 'nextbike_trips_end_at_station_count', 'current_temp', 'current_precipitation_volume'])

/tmp/ipykernel_2575952/41814695.py:51: RuntimeWarning: invalid value encountered in scalar divide
  qd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:55: RuntimeWarning: invalid value encountered in scalar divide
  cvqd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:51: RuntimeWarning: invalid value encountered in scalar divide
  qd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:55: RuntimeWarning: invalid value encountered in scalar divide
  cvqd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:51: RuntimeWarning: invalid value encountered in scalar divide
  qd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:55: RuntimeWarning: invalid value encountered in scalar divide
  cvqd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:51: RuntimeWarning: invalid value encountered in scalar divide
  qd = iqr / (percentile_75 + percenti

column                                        tier_trips_count  \
rows                                                     29190   
sum                                                        228   
mean                                                  0.007811   
median                                                     0.0   
mode               0    0
Name: tier_trips_count, dtype: int64   
max                                                          2   
min                                                          0   
std_dev                                               0.089195   
variance                                              0.007956   
skewness                                             11.614165   
kurtosis                                             139.06087   
percentile_25                                              0.0   
percentile_75                                              0.0   
iqr                                                        0.0   
range                                                        2   
cv                                                   11.419277   
qd                                                         NaN   
cs                                                  130.211278   
ck                                                 1559.069822   
cvs                                                 130.211278   
cvk                                                1559.069822   
cvcs                                                130.211278   
cvck                                               1559.069822   
cvcv                                                 11.419277   
cvqd                                                       NaN   
cvr                                                 256.052632   
cvm                                                        1.0   
cvmed                                                      0.0   
cvmode         0    0.0
Name: tier_trips_count, dtype: float64   

column                           tier_trips_end_at_station_count  \
rows                                                       29190   
sum                                                          195   
mean                                                     0.00668   
median                                                       0.0   
mode           0    0
Name: tier_trips_end_at_station_count, ...   
max                                                            2   
min                                                            0   
std_dev                                                 0.081881   
variance                                                0.006704   
skewness                                               12.299317   
kurtosis                                              152.270711   
percentile_25                                                0.0   
percentile_75                                                0.0   
iqr                                                          0.0   
range                                                          2   
cv                                                     12.256947   
qd                                                           NaN   
cs                                                    150.209766   
ck                                                   1859.659945   
cvs                                                   150.209766   
cvk                                                  1859.659945   
cvcs                                                  150.209766   
cvck                                                 1859.659945   
cvcv                                                   12.256947   
cvqd                                                         NaN   
cvr                                                   299.384615   
cvm                                                          1.0   
cvmed                                                        0.0   
cvmode         0    0.0
Name: tier_trips_end_at

In [349]:
early_morning_delay_tier = check_micromobility_datasets('tier', early_morning_delay)

In [350]:
early_morning_delay_tier.describe()

tier_trips_id          tier_trips_start_time  \
count   1.750000e+02                            175   
mean    7.958681e+08  2023-07-14 08:59:49.714285568   
min     7.822657e+08            2023-07-01 03:20:00   
25%     7.823440e+08            2023-07-08 03:22:30   
50%     7.824499e+08            2023-07-13 05:20:00   
75%     8.087270e+08            2023-07-20 05:25:00   
max     8.322841e+08            2023-07-31 05:55:00   
std     1.598417e+07                            NaN   

                 tier_trips_end_time              trip_duration  \
count                            175                        175   
mean   2023-07-14 09:13:11.999999744  0 days 00:13:22.285714285   
min              2023-07-01 03:35:00            0 days 00:05:00   
25%              2023-07-08 03:32:30            0 days 00:10:00   
50%              2023-07-13 05:25:00            0 days 00:10:00   
75%              2023-07-20 05:35:00            0 days 00:15:00   
max              2023-07-31 06:05:00            0 days 01:15:00   
std                              NaN  0 days 00:08:27.750763109   

       trip_distance_kilometers  trip_distance_meters  start_stop_id  \
count                175.000000            175.000000     133.000000   
mean                   1.732297           1732.297117    1447.000000   
min                    0.106767            106.767059     161.000000   
25%                    0.784239            784.239451    1106.000000   
50%                    1.406742           1406.741766    1140.000000   
75%                    2.358062           2358.061683    1500.000000   
max                    5.989840           5989.839742    9703.000000   
std                    1.295188           1295.188150    1509.245316   

       end_stop_id  trip_duration_seconds  
count   103.000000             175.000000  
mean   1255.300971             802.285714  
min      43.000000             300.000000  
25%     696.000000             600.000000  
50%    1115.000000             600.000000  
75%    1312.000000             900.000000  
max    9073.000000            4500.000000  
std    1123.450295             507.750763

In [351]:
get_stats(early_morning_delay_tier, ['trip_duration_seconds', 'trip_distance_kilometers'])

column                                     trip_duration_seconds  \
rows                                                         175   
sum                                                     140400.0   
mean                                                  802.285714   
median                                                     600.0   
mode           0    600.0
Name: trip_duration_seconds, dtype:...   
max                                                       4500.0   
min                                                        300.0   
std_dev                                               507.750763   
variance                                           257810.837438   
skewness                                                3.264051   
kurtosis                                                18.42665   
percentile_25                                              600.0   
percentile_75                                              900.0   
iqr                                                        300.0   
range                                                     4200.0   
cv                                                       0.63288   
qd                                                           0.2   
cs                                                      0.006428   
ck                                                      0.036291   
cvs                                                     0.006428   
cvk                                                     0.036291   
cvcs                                                    0.006428   
cvck                                                    0.036291   
cvcv                                                     0.63288   
cvqd                                                         0.2   
cvr                                                     5.235043   
cvm                                                          1.0   
cvmed                                                   0.747863   
cvmode         0    0.747863
Name: trip_duration_seconds, dty...   

column                                  trip_distance_kilometers  
rows                                                         175  
sum                                                   303.151995  
mean                                                    1.732297  
median                                                  1.406742  
mode           0      0.106767
1      0.117351
2      0.18990...  
max                                                      5.98984  
min                                                     0.106767  
std_dev                                                 1.295188  
variance                                                1.677512  
skewness                                                1.450411  
kurtosis                                                2.077655  
percentile_25                                           0.784239  
percentile_75                                           2.358062  
iqr                                                     1.573822  
range                                                   5.883073  
cv                                                      0.747671  
qd                                                       0.50085  
cs                                                      1.119846  
ck                                                      1.604134  
cvs                                                     1.119846  
cvk                                                     1.604134  
cvcs                                                    1.119846  
cvck                                                    1.604134  
cvcv                                                    0.747671  
cvqd                                                     0.50085  
cvr                                                     3.396111  
cvm                                                          1.0  
cvmed                                                   0.812067  
cvmode         0

In [352]:
# get entries where trips start and end at station
early_morning_delay_tier_station_station = early_morning_delay_tier[early_morning_delay_tier['end_stop_id'].notna() & early_morning_delay_tier['start_stop_id'].notna()]
early_morning_delay_tier_station_station

tier_trips_id tier_trips_start_time tier_trips_end_time vehicle type  \
3238195      782417418   2023-07-02 03:45:00 2023-07-02 03:55:00    e-scooter   
3273838      782449853   2023-07-02 05:15:00 2023-07-02 05:25:00    e-scooter   
3178661      782362419   2023-07-04 04:00:00 2023-07-04 04:20:00    e-scooter   
3249718      782427929   2023-07-04 05:30:00 2023-07-04 05:50:00    e-scooter   
3170469      782354952   2023-07-04 05:35:00 2023-07-04 05:50:00    e-scooter   
...                ...                   ...                 ...          ...   
3338301      832133583   2023-07-29 05:15:00 2023-07-29 05:45:00    e-scooter   
3482091      832262447   2023-07-29 05:15:00 2023-07-29 05:25:00    e-scooter   
3482724      832263056   2023-07-30 04:45:00 2023-07-30 04:50:00    e-scooter   
3504669      832284107   2023-07-30 05:55:00 2023-07-30 06:05:00    e-scooter   
3410445      832193686   2023-07-31 05:10:00 2023-07-31 05:15:00    e-scooter   

          trip_duration  trip_distance_kilometers  trip_distance_meters  \
3238195 0 days 00:10:00                  1.411129           1411.128592   
3273838 0 days 00:10:00                  2.022794           2022.794306   
3178661 0 days 00:20:00                  2.578002           2578.001637   
3249718 0 days 00:20:00                  1.829930           1829.930216   
3170469 0 days 00:15:00                  1.858566           1858.565527   
...                 ...                       ...                   ...   
3338301 0 days 00:30:00                  4.841966           4841.965856   
3482091 0 days 00:10:00                  0.399588            399.587965   
3482724 0 days 00:05:00                  1.594961           1594.961380   
3504669 0 days 00:10:00                  0.897729            897.728955   
3410445 0 days 00:05:00                  0.410750            410.750398   

         start_stop_id                            start_stop_name  \
3238195          699.0       Bonn Hochkreuz/Deutsches Museum Bonn   
3273838         1585.0                           Bonn Küdinghoven   
3178661         1176.0                           Bonn Husarenstr.   
3249718         1255.0                Bonn Graf-Stauffenberg-Str.   
3170469         1102.0                         Bonn Friedensplatz   
...                ...                                        ...   
3338301         1115.0  Bonn Bertha-Von-Suttner-Pl./Beethovenhaus   
3482091         1115.0  Bonn Bertha-Von-Suttner-Pl./Beethovenhaus   
3482724         1500.0                 Bonn Konrad-Adenauer-Platz   
3504669         1104.0                             Bonn Stadthaus   
3410445          694.0                     Bonn Tannenbusch Mitte   

                                         start_buffer_zone  end_stop_id  \
3238195  801621     POLYGON ((7.157885983913106 50.7227...        690.0   
3273838  801621     POLYGON ((7.157885983913106 50.7227...       1504.0   
3178661  801621     POLYGON ((7.157885983913106 50.7227...       1406.0   
3249718  801621     POLYGON ((7.157885983913106 50.7227...        686.0   
3170469  801621     POLYGON ((7.157885983913106 50.7227...       1221.0   
...                                                    ...          ...   
3338301  801621     POLYGON ((7.157885983913106 50.7227...        696.0   
3482091  801621     POLYGON ((7.157885983913106 50.7227...       1102.0   
3482724  801621     POLYGON ((7.157885983913106 50.7227...       1115.0   
3504669  801621     POLYGON ((7.157885983913106 50.7227...       1135.0   
3410445  801621     POLYGON ((7.157885983913106 50.7227...        694.0   

                                     end_stop_name  \
3238195                      Bonn Olof-Palme-Allee   
3273838                              Bonn Beuel Bf   
3178661                     Bonn Kopenhagener Str.   
3249718                     Bonn Universität/Markt   
3170469                          Bonn Kaufmannstr.   
...                                            ...   
3338301                 Bon

In [353]:
early_morning_delay_tier_station_station.describe()

tier_trips_id          tier_trips_start_time  \
count   9.000000e+01                             90   
mean    7.953758e+08  2023-07-13 22:40:13.333333504   
min     7.822657e+08            2023-07-02 03:45:00   
25%     7.823275e+08            2023-07-07 11:16:15   
50%     7.824288e+08            2023-07-12 05:37:30   
75%     8.087211e+08            2023-07-19 05:52:30   
max     8.322841e+08            2023-07-31 05:10:00   
std     1.554786e+07                            NaN   

                 tier_trips_end_time              trip_duration  \
count                             90                         90   
mean   2023-07-13 22:52:53.333333504            0 days 00:12:40   
min              2023-07-02 03:55:00            0 days 00:05:00   
25%              2023-07-07 11:22:30            0 days 00:10:00   
50%              2023-07-12 05:47:30            0 days 00:10:00   
75%              2023-07-19 06:01:15            0 days 00:15:00   
max              2023-07-31 05:15:00            0 days 01:15:00   
std                              NaN  0 days 00:09:36.272407495   

       trip_distance_kilometers  trip_distance_meters  start_stop_id  \
count                 90.000000             90.000000      90.000000   
mean                   1.416719           1416.718956    1320.655556   
min                    0.106767            106.767059     683.000000   
25%                    0.653821            653.821064    1104.500000   
50%                    1.122020           1122.020206    1115.000000   
75%                    1.881747           1881.746913    1223.000000   
max                    4.841966           4841.965856    8950.000000   
std                    0.984349            984.348638    1143.598796   

       end_stop_id  trip_duration_seconds  
count    90.000000              90.000000  
mean   1284.933333             760.000000  
min     684.000000             300.000000  
25%     696.750000             600.000000  
50%    1115.000000             600.000000  
75%    1222.500000             900.000000  
max    9073.000000            4500.000000  
std    1184.616022             576.272407

In [354]:
# get statistics for the tier trips that start and end at a station
get_stats(early_morning_delay_tier_station_station, ['trip_duration_seconds', 'trip_distance_kilometers'])

column                                     trip_duration_seconds  \
rows                                                          90   
sum                                                      68400.0   
mean                                                       760.0   
median                                                     600.0   
mode           0    600.0
Name: trip_duration_seconds, dtype:...   
max                                                       4500.0   
min                                                        300.0   
std_dev                                               576.272407   
variance                                            332089.88764   
skewness                                                4.135659   
kurtosis                                               23.059301   
percentile_25                                              600.0   
percentile_75                                              900.0   
iqr                                                        300.0   
range                                                     4200.0   
cv                                                      0.758253   
qd                                                           0.2   
cs                                                      0.007177   
ck                                                      0.040015   
cvs                                                     0.007177   
cvk                                                     0.040015   
cvcs                                                    0.007177   
cvck                                                    0.040015   
cvcv                                                    0.758253   
cvqd                                                         0.2   
cvr                                                     5.526316   
cvm                                                          1.0   
cvmed                                                   0.789474   
cvmode         0    0.789474
Name: trip_duration_seconds, dty...   

column                                  trip_distance_kilometers  
rows                                                          90  
sum                                                   127.504706  
mean                                                    1.416719  
median                                                   1.12202  
mode           0     0.106767
1     0.189906
2     0.247372
3...  
max                                                     4.841966  
min                                                     0.106767  
std_dev                                                 0.984349  
variance                                                0.968942  
skewness                                                1.067475  
kurtosis                                                0.713402  
percentile_25                                           0.653821  
percentile_75                                           1.881747  
iqr                                                     1.227926  
range                                                   4.735199  
cv                                                      0.694809  
qd                                                       0.48428  
cs                                                      1.084448  
ck                                                      0.724746  
cvs                                                     1.084448  
cvk                                                     0.724746  
cvcs                                                    1.084448  
cvck                                                    0.724746  
cvcv                                                    0.694809  
cvqd                                                     0.48428  
cvr                                                      3.34237  
cvm                                                          1.0  
cvmed                                                   0.791985  
cvmode         0

In [355]:
early_morning_delay_next = check_micromobility_datasets('next', early_morning_delay)

In [356]:
early_morning_delay_next.describe()

nextbike_trips_id      nextbike_trips_start_time  \
count       5.030000e+02                            503   
mean        3.794707e+07  2023-07-14 18:45:36.143141120   
min         3.771654e+07            2023-07-01 05:16:00   
25%         3.783723e+07            2023-07-07 05:41:00   
50%         3.795222e+07            2023-07-13 05:51:00   
75%         3.806046e+07            2023-07-20 06:01:00   
max         3.817124e+07            2023-07-31 06:01:00   
std         1.272459e+05                            NaN   

             nextbike_trips_end_time              trip_duration  \
count                            503                        503   
mean   2023-07-14 18:59:43.658051584  0 days 00:14:07.514910536   
min              2023-07-01 05:46:00            0 days 00:05:00   
25%              2023-07-07 05:58:30            0 days 00:10:00   
50%              2023-07-13 06:06:00            0 days 00:15:00   
75%              2023-07-20 06:18:30            0 days 00:15:00   
max              2023-07-31 06:16:00            0 days 00:45:00   
std                              NaN  0 days 00:06:33.711508934   

       trip_distance_kilometers  trip_distance_meters  start_stop_id  \
count                503.000000            503.000000     367.000000   
mean                   1.932618           1932.617801    1443.923706   
min                    0.100540            100.539565     161.000000   
25%                    0.867420            867.420134    1115.000000   
50%                    1.586179           1586.178621    1161.000000   
75%                    2.604084           2604.083886    1255.000000   
max                    9.506986           9506.985634    9703.000000   
std                    1.490944           1490.943907    1491.705332   

       end_stop_id  trip_duration_seconds  
count   316.000000             503.000000  
mean   1031.784810             847.514911  
min      43.000000             300.000000  
25%     687.000000             600.000000  
50%    1102.000000             900.000000  
75%    1192.000000             900.000000  
max    8507.000000            2700.000000  
std     765.198859             393.711509

In [357]:
get_stats(early_morning_delay_next, ['trip_duration_seconds', 'trip_distance_kilometers'])

column                                     trip_duration_seconds  \
rows                                                         503   
sum                                                     426300.0   
mean                                                  847.514911   
median                                                     900.0   
mode           0    600.0
Name: trip_duration_seconds, dtype:...   
max                                                       2700.0   
min                                                        300.0   
std_dev                                               393.711509   
variance                                           155008.752267   
skewness                                                1.419681   
kurtosis                                                 3.53585   
percentile_25                                              600.0   
percentile_75                                              900.0   
iqr                                                        300.0   
range                                                     2400.0   
cv                                                      0.464548   
qd                                                           0.2   
cs                                                      0.003606   
ck                                                      0.008981   
cvs                                                     0.003606   
cvk                                                     0.008981   
cvcs                                                    0.003606   
cvck                                                    0.008981   
cvcv                                                    0.464548   
cvqd                                                         0.2   
cvr                                                     2.831809   
cvm                                                          1.0   
cvmed                                                   1.061928   
cvmode         0    0.707952
Name: trip_duration_seconds, dty...   

column                                  trip_distance_kilometers  
rows                                                         503  
sum                                                   972.106754  
mean                                                    1.932618  
median                                                  1.586179  
mode           0    0.982570
1    1.635495
Name: trip_distanc...  
max                                                     9.506986  
min                                                      0.10054  
std_dev                                                 1.490944  
variance                                                2.222914  
skewness                                                1.663053  
kurtosis                                                3.828459  
percentile_25                                            0.86742  
percentile_75                                           2.604084  
iqr                                                     1.736664  
range                                                   9.406446  
cv                                                      0.771463  
qd                                                      0.500263  
cs                                                      1.115436  
ck                                                      2.567809  
cvs                                                     1.115436  
cvk                                                     2.567809  
cvcs                                                    1.115436  
cvck                                                    2.567809  
cvcv                                                    0.771463  
cvqd                                                    0.500263  
cvr                                                     4.867205  
cvm                                                          1.0  
cvmed                                                   0.820741  
cvmode         0

In [358]:
# get entries where trips start and end at station
early_morning_delay_next_station_station = early_morning_delay_next[early_morning_delay_next['end_stop_id'].notna() & early_morning_delay_next['start_stop_id'].notna()]
early_morning_delay_next_station_station

nextbike_trips_id nextbike_trips_start_time nextbike_trips_end_time  \
1417189           37961351       2023-07-01 05:41:00     2023-07-01 05:56:00   
1220393           37717932       2023-07-01 05:56:00     2023-07-01 06:11:00   
1218972           37716538       2023-07-03 04:51:00     2023-07-03 05:01:00   
1658596           37790015       2023-07-03 05:06:00     2023-07-03 05:16:00   
1471548           38036106       2023-07-03 05:16:00     2023-07-03 05:31:00   
...                    ...                       ...                     ...   
1590493           37752725       2023-07-31 05:41:00     2023-07-31 05:46:00   
1348193           37901791       2023-07-31 05:56:00     2023-07-31 06:06:00   
1280462           37868628       2023-07-31 05:56:00     2023-07-31 06:06:00   
1386255           37922279       2023-07-31 05:56:00     2023-07-31 06:06:00   
1265304           37741762       2023-07-31 06:01:00     2023-07-31 06:16:00   

         nextbike_trips_start_at_station  nextbike_trips_end_at_station  \
1417189                            False                          False   
1220393                            False                          False   
1218972                            False                          False   
1658596                            False                          False   
1471548                            False                          False   
...                                  ...                            ...   
1590493                            False                          False   
1348193                            False                          False   
1280462                            False                          False   
1386255                            False                          False   
1265304                            False                          False   

        vehicle type   trip_duration  trip_distance_kilometers  \
1417189         bike 0 days 00:15:00                  1.671334   
1220393         bike 0 days 00:15:00                  1.377444   
1218972         bike 0 days 00:10:00                  1.534328   
1658596         bike 0 days 00:10:00                  0.929705   
1471548         bike 0 days 00:15:00                  3.080515   
...              ...             ...                       ...   
1590493         bike 0 days 00:05:00                  0.386656   
1348193         bike 0 days 00:10:00                  1.470388   
1280462         bike 0 days 00:10:00                  0.938190   
1386255         bike 0 days 00:10:00                  0.985174   
1265304         bike 0 days 00:15:00                  1.083682   

         trip_distance_meters  \
1417189           1671.334291   
1220393           1377.444442   
1218972           1534.328341   
1658596            929.705305   
1471548           3080.515217   
...                       ...   
1590493            386.656209   
1348193           1470.387556   
1280462            938.190043   
1386255            985.174223   
1265304           1083.682421   

                                            start_location  \
1417189  b'\x01\x01\x00\x00\x00\xd9\n\x9a\x96XY\x1c@"\x...   
1220393  b'\x01\x01\x00\x00\x00\xcfj\x81=&R\x1c@\x7f\xa...   
1218972  b'\x01\x01\x00\x00\x00\xac\xad\xd8_vo\x1c@\x1e...   
1658596  b'\x01\x01\x00\x00\x00\x833\xf8\xfb\xc5l\x1c@\...   
1471548  b'\x01\x01\x00\x00\x00\xf5*2: i\x1c@F\xce\xc2\...   
...                                                    ...   
1590493  b'\x01\x01\x00\x00\x005)\x05\xdd^2\x1c@k}\x91\...   
1348193  b'\x01\x01\x00\x00\x00\x8b3\x869A[\x1c@\x15\xa...   
1280462  b'\x01\x01\x00\x00\x00\xf7V$&\xa8Q\x1c@p\x08Uj...   
1386255  b'\x01\x01\x00\x00\x00\x15p\xcf\xf3\xa7]\x1c@\...   
1265304  b'\x01\x01\x00\x00\x00\x86\x8d\xb2~3a\x1c@\xb4...   

                                              end_location  start_stop_id  \
1417189  b'\x01\x01\x00\x00\x00\x82\x8d\xeb\xdf\xf5I\x1...         1151.0   
1220393  b'\x01\x01\x00\x00\x00\x9f\xe4\x0e\x9b\xc8L\x1...

In [359]:
early_morning_delay_next_station_station.describe()

nextbike_trips_id      nextbike_trips_start_time  \
count       2.360000e+02                            236   
mean        3.794298e+07  2023-07-14 01:41:16.525424128   
min         3.771654e+07            2023-07-01 05:41:00   
25%         3.783827e+07            2023-07-06 05:56:00   
50%         3.793847e+07            2023-07-12 05:36:00   
75%         3.805475e+07            2023-07-20 05:09:45   
max         3.816145e+07            2023-07-31 06:01:00   
std         1.285784e+05                            NaN   

             nextbike_trips_end_time              trip_duration  \
count                            236                        236   
mean   2023-07-14 01:54:01.779661056  0 days 00:12:45.254237288   
min              2023-07-01 05:56:00            0 days 00:05:00   
25%              2023-07-06 06:11:00            0 days 00:10:00   
50%              2023-07-12 05:53:30            0 days 00:10:00   
75%              2023-07-20 05:23:30            0 days 00:15:00   
max              2023-07-31 06:16:00            0 days 00:40:00   
std                              NaN  0 days 00:05:20.605044662   

       trip_distance_kilometers  trip_distance_meters  start_stop_id  \
count                236.000000            236.000000     236.000000   
mean                   1.514143           1514.143268    1511.491525   
min                    0.100540            100.539565     161.000000   
25%                    0.793974            793.973500    1115.000000   
50%                    1.306646           1306.646451    1162.000000   
75%                    1.911415           1911.414734    1241.250000   
max                    5.624807           5624.806754    9703.000000   
std                    1.079487           1079.487298    1633.222220   

       end_stop_id  trip_duration_seconds  
count   236.000000             236.000000  
mean   1058.508475             765.254237  
min      43.000000             300.000000  
25%     687.000000             600.000000  
50%    1102.500000             600.000000  
75%    1179.250000             900.000000  
max    8507.000000            2400.000000  
std     856.690418             320.605045

In [360]:
# get statistics for the tier trips that start and end at a station
get_stats(early_morning_delay_next_station_station, ['trip_duration_seconds', 'trip_distance_kilometers'])

column                                     trip_duration_seconds  \
rows                                                         236   
sum                                                     180600.0   
mean                                                  765.254237   
median                                                     600.0   
mode           0    600.0
Name: trip_duration_seconds, dtype:...   
max                                                       2400.0   
min                                                        300.0   
std_dev                                               320.605045   
variance                                           102787.594663   
skewness                                                1.163981   
kurtosis                                                2.785538   
percentile_25                                              600.0   
percentile_75                                              900.0   
iqr                                                        300.0   
range                                                     2100.0   
cv                                                      0.418952   
qd                                                           0.2   
cs                                                      0.003631   
ck                                                      0.008688   
cvs                                                     0.003631   
cvk                                                     0.008688   
cvcs                                                    0.003631   
cvck                                                    0.008688   
cvcv                                                    0.418952   
cvqd                                                         0.2   
cvr                                                     2.744186   
cvm                                                          1.0   
cvmed                                                   0.784053   
cvmode         0    0.784053
Name: trip_duration_seconds, dty...   

column                                  trip_distance_kilometers  
rows                                                         236  
sum                                                   357.337811  
mean                                                    1.514143  
median                                                  1.306646  
mode           0    0.982570
1    1.635495
Name: trip_distanc...  
max                                                     5.624807  
min                                                      0.10054  
std_dev                                                 1.079487  
variance                                                1.165293  
skewness                                                1.551692  
kurtosis                                                2.719592  
percentile_25                                           0.793974  
percentile_75                                           1.911415  
iqr                                                     1.117441  
range                                                   5.524267  
cv                                                      0.712936  
qd                                                      0.413043  
cs                                                      1.437435  
ck                                                      2.519337  
cvs                                                     1.437435  
cvk                                                     2.519337  
cvcs                                                    1.437435  
cvck                                                    2.519337  
cvcv                                                    0.712936  
cvqd                                                    0.413043  
cvr                                                     3.648444  
cvm                                                          1.0  
cvmed                                                   0.862961  
cvmode         0

In [361]:
early_morning_no_delay = no_delay[(no_delay['scheduled_arrival_time'].dt.hour > 2) & (no_delay['scheduled_arrival_time'].dt.hour < 6)]
early_morning_no_delay

route_id  agency_id route_short_name  route_type route_type_name  \
16            551          8              551           3             Bus   
17            551          8              551           3             Bus   
18            551          8              551           3             Bus   
19            551          8              551           3             Bus   
20            551          8              551           3             Bus   
...           ...        ...              ...         ...             ...   
2564809       688          6               N8           3             Bus   
2564811       687          6               N7           3             Bus   
2564817       684          6               N4           3             Bus   
2564834       689          6               N9           3             Bus   
2564845       688          6               N8           3             Bus   

                                      agency_name  service_id  \
16       RSVG Rhein-Sieg-Verkehrsgesellschaft mbH         125   
17       RSVG Rhein-Sieg-Verkehrsgesellschaft mbH         125   
18       RSVG Rhein-Sieg-Verkehrsgesellschaft mbH         125   
19       RSVG Rhein-Sieg-Verkehrsgesellschaft mbH         125   
20       RSVG Rhein-Sieg-Verkehrsgesellschaft mbH         125   
...                                           ...         ...   
2564809         SWB Stadtwerke Bonn Verkehrs GmbH         179   
2564811         SWB Stadtwerke Bonn Verkehrs GmbH         179   
2564817         SWB Stadtwerke Bonn Verkehrs GmbH         179   
2564834         SWB Stadtwerke Bonn Verkehrs GmbH          43   
2564845         SWB Stadtwerke Bonn Verkehrs GmbH         179   

                                                   trip_id  \
16       254-551-008-2071.2.22:023200-34-157_33C7EAED-7...   
17       254-551-008-2071.2.22:023200-34-157_33C7EAED-7...   
18       254-551-008-2071.2.22:023200-34-157_33C7EAED-7...   
19       254-551-008-2071.2.22:023200-34-157_33C7EAED-7...   
20       254-551-008-2071.2.22:023200-34-157_33C7EAED-7...   
...                                                    ...   
2564809  6880005-688-006-687.2.32:263500-36-1_5350170A-...   
2564811  6870005-687-006-687.2.24:263500-34-1_F0CE2D00-...   
2564817  6840005-684-006-687.2.32:263500-36-1_7F56FE12-...   
2564834  6890005-689-006-687.2.34:263500-53-1_2AFE8F0F-...   
2564845  6880005-688-006-687.2.32:263500-36-1_5350170A-...   

                         trip_headsign  direction_id  ...  delay_span  \
16                            Bonn Hbf             1  ...           0   
17                            Bonn Hbf             1  ...           0   
18                            Bonn Hbf             1  ...           0   
19                            Bonn Hbf             1  ...           0   
20                            Bonn Hbf             1  ...           0   
...                                ...           ...  ...         ...   
2564809                       Bonn Hbf             0  ...           0   
2564811  Bad Godesberg Bf / Rheinallee             0  ...           0   
2564817                    Am Waldrand             0  ...           0   
2564834                       Bonn Hbf             0  ...           0   
2564845                       Bonn Hbf             0  ...           0   

         arrival_delay_span weather_int time_span_arrival  \
16                        0           0                 0   
17                        0           0                 0   
18                        0           0                 0   
19                        0           0                 0   
20                        0           0                 0   
...                     ...         ...               ...   
2564809                   0           1     early morning   
2564811                   0           1     early morning   
2564817                   0           1     early morning   
2564834                   0           1     early morning   
2564845   

In [362]:
get_stats(early_morning_no_delay, ['tier_trips_count', 'tier_trips_end_at_station_count', 'nextbike_trips_count', 'nextbike_trips_end_at_station_count', 'current_temp', 'current_precipitation_volume'])

/tmp/ipykernel_2575952/41814695.py:51: RuntimeWarning: invalid value encountered in scalar divide
  qd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:55: RuntimeWarning: invalid value encountered in scalar divide
  cvqd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:51: RuntimeWarning: invalid value encountered in scalar divide
  qd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:55: RuntimeWarning: invalid value encountered in scalar divide
  cvqd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:51: RuntimeWarning: invalid value encountered in scalar divide
  qd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:55: RuntimeWarning: invalid value encountered in scalar divide
  cvqd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:51: RuntimeWarning: invalid value encountered in scalar divide
  qd = iqr / (percentile_75 + percenti

column                                        tier_trips_count  \
rows                                                     20057   
sum                                                        323   
mean                                                  0.016104   
median                                                     0.0   
mode               0    0
Name: tier_trips_count, dtype: int64   
max                                                          2   
min                                                          0   
std_dev                                               0.129009   
variance                                              0.016643   
skewness                                              8.239675   
kurtosis                                             71.114791   
percentile_25                                              0.0   
percentile_75                                              0.0   
iqr                                                        0.0   
range                                                        2   
cv                                                    8.010939   
qd                                                         NaN   
cs                                                   63.869005   
ck                                                  551.239067   
cvs                                                  63.869005   
cvk                                                 551.239067   
cvcs                                                 63.869005   
cvck                                                551.239067   
cvcv                                                  8.010939   
cvqd                                                       NaN   
cvr                                                  124.19195   
cvm                                                        1.0   
cvmed                                                      0.0   
cvmode         0    0.0
Name: tier_trips_count, dtype: float64   

column                           tier_trips_end_at_station_count  \
rows                                                       20057   
sum                                                          292   
mean                                                    0.014559   
median                                                       0.0   
mode           0    0
Name: tier_trips_end_at_station_count, ...   
max                                                            2   
min                                                            0   
std_dev                                                 0.121844   
variance                                                0.014846   
skewness                                                8.516391   
kurtosis                                               74.761105   
percentile_25                                                0.0   
percentile_75                                                0.0   
iqr                                                          0.0   
range                                                          2   
cv                                                      8.369241   
qd                                                           NaN   
cs                                                     69.896051   
ck                                                    613.582238   
cvs                                                    69.896051   
cvk                                                   613.582238   
cvcs                                                   69.896051   
cvck                                                  613.582238   
cvcv                                                    8.369241   
cvqd                                                         NaN   
cvr                                                   137.376712   
cvm                                                          1.0   
cvmed                                                        0.0   
cvmode         0    0.0
Name: tier_trips_end_at

In [363]:
early_morning_no_delay_tier = check_micromobility_datasets('tier', early_morning_no_delay)

In [364]:
early_morning_no_delay_tier.describe()

tier_trips_id          tier_trips_start_time  \
count   1.850000e+02                            185   
mean    7.952657e+08  2023-07-14 11:31:17.837837824   
min     7.822657e+08            2023-07-01 03:30:00   
25%     7.823400e+08            2023-07-08 03:45:00   
50%     7.824287e+08            2023-07-13 04:35:00   
75%     8.087317e+08            2023-07-21 05:10:00   
max     8.323063e+08            2023-07-31 05:45:00   
std     1.604155e+07                            NaN   

                 tier_trips_end_time              trip_duration  \
count                            185                        185   
mean   2023-07-14 11:44:38.918919168  0 days 00:13:21.081081081   
min              2023-07-01 03:45:00            0 days 00:05:00   
25%              2023-07-08 04:05:00            0 days 00:10:00   
50%              2023-07-13 04:40:00            0 days 00:10:00   
75%              2023-07-21 05:20:00            0 days 00:15:00   
max              2023-07-31 05:55:00            0 days 01:15:00   
std                              NaN  0 days 00:08:00.939884744   

       trip_distance_kilometers  trip_distance_meters  start_stop_id  \
count                185.000000            185.000000     157.000000   
mean                   1.761637           1761.636530    1139.464968   
min                    0.104447            104.447092      43.000000   
25%                    0.741660            741.659744     687.000000   
50%                    1.445138           1445.137841    1106.000000   
75%                    2.363418           2363.417558    1500.000000   
max                    7.547788           7547.787527    9478.000000   
std                    1.432010           1432.010271     992.789359   

       end_stop_id  trip_duration_seconds  
count   126.000000             185.000000  
mean   1316.769841             801.081081  
min      43.000000             300.000000  
25%    1102.000000             600.000000  
50%    1131.000000             600.000000  
75%    1399.250000             900.000000  
max    8507.000000            4500.000000  
std    1191.406941             480.939885

In [365]:
get_stats(early_morning_no_delay_tier, ['trip_duration_seconds', 'trip_distance_kilometers'])

column                                     trip_duration_seconds  \
rows                                                         185   
sum                                                     148200.0   
mean                                                  801.081081   
median                                                     600.0   
mode           0    600.0
Name: trip_duration_seconds, dtype:...   
max                                                       4500.0   
min                                                        300.0   
std_dev                                               480.939885   
variance                                           231303.172738   
skewness                                                3.199617   
kurtosis                                               18.881961   
percentile_25                                              600.0   
percentile_75                                              900.0   
iqr                                                        300.0   
range                                                     4200.0   
cv                                                      0.600364   
qd                                                           0.2   
cs                                                      0.006653   
ck                                                      0.039261   
cvs                                                     0.006653   
cvk                                                     0.039261   
cvcs                                                    0.006653   
cvck                                                    0.039261   
cvcv                                                    0.600364   
cvqd                                                         0.2   
cvr                                                     5.242915   
cvm                                                          1.0   
cvmed                                                   0.748988   
cvmode         0    0.748988
Name: trip_duration_seconds, dty...   

column                                  trip_distance_kilometers  
rows                                                         185  
sum                                                   325.902758  
mean                                                    1.761637  
median                                                  1.445138  
mode           0      0.104447
1      0.150769
2      0.17596...  
max                                                     7.547788  
min                                                     0.104447  
std_dev                                                  1.43201  
variance                                                2.050653  
skewness                                                1.677374  
kurtosis                                                3.138471  
percentile_25                                            0.74166  
percentile_75                                           2.363418  
iqr                                                     1.621758  
range                                                    7.44334  
cv                                                      0.812886  
qd                                                      0.522292  
cs                                                      1.171342  
ck                                                      2.191654  
cvs                                                     1.171342  
cvk                                                     2.191654  
cvcs                                                    1.171342  
cvck                                                    2.191654  
cvcv                                                    0.812886  
cvqd                                                    0.522292  
cvr                                                     4.225242  
cvm                                                          1.0  
cvmed                                                   0.820338  
cvmode         0

In [366]:
# get entries where trips start and end at station
early_morning_no_delay_tier_station_station = early_morning_no_delay_tier[early_morning_no_delay_tier['end_stop_id'].notna() & early_morning_no_delay_tier['start_stop_id'].notna()]
early_morning_no_delay_tier_station_station

tier_trips_id tier_trips_start_time tier_trips_end_time vehicle type  \
2973348      782286043   2023-07-01 04:35:00 2023-07-01 04:50:00    e-scooter   
3194413      782376718   2023-07-01 05:55:00 2023-07-01 06:05:00    e-scooter   
3041112      782306453   2023-07-02 05:50:00 2023-07-02 06:00:00    e-scooter   
3075830      782318166   2023-07-04 04:45:00 2023-07-04 04:55:00    e-scooter   
3211655      782393209   2023-07-04 05:15:00 2023-07-04 05:25:00    e-scooter   
...                ...                   ...                 ...          ...   
3482091      832262447   2023-07-29 05:15:00 2023-07-29 05:25:00    e-scooter   
3482724      832263056   2023-07-30 04:45:00 2023-07-30 04:50:00    e-scooter   
3410446      832193687   2023-07-31 05:25:00 2023-07-31 05:30:00    e-scooter   
3305644      832111334   2023-07-31 05:30:00 2023-07-31 05:40:00    e-scooter   
3376380      832161003   2023-07-31 05:45:00 2023-07-31 05:55:00    e-scooter   

          trip_duration  trip_distance_kilometers  trip_distance_meters  \
2973348 0 days 00:15:00                  3.658388           3658.388003   
3194413 0 days 00:10:00                  0.177056            177.056127   
3041112 0 days 00:10:00                  2.363298           2363.298081   
3075830 0 days 00:10:00                  0.732924            732.924345   
3211655 0 days 00:10:00                  0.908268            908.267654   
...                 ...                       ...                   ...   
3482091 0 days 00:10:00                  0.399588            399.587965   
3482724 0 days 00:05:00                  1.594961           1594.961380   
3410446 0 days 00:05:00                  0.566245            566.244843   
3305644 0 days 00:10:00                  0.741660            741.659744   
3376380 0 days 00:10:00                  0.999367            999.366812   

         start_stop_id                            start_stop_name  \
2973348          687.0                                   Bonn Hbf   
3194413          701.0                   Bonn Plittersdorfer Str.   
3041112         1500.0                 Bonn Konrad-Adenauer-Platz   
3075830          687.0                                   Bonn Hbf   
3211655         1500.0                 Bonn Konrad-Adenauer-Platz   
...                ...                                        ...   
3482091         1115.0  Bonn Bertha-Von-Suttner-Pl./Beethovenhaus   
3482724         1500.0                 Bonn Konrad-Adenauer-Platz   
3410446          694.0                     Bonn Tannenbusch Mitte   
3305644          687.0                                   Bonn Hbf   
3376380          687.0                                   Bonn Hbf   

                                         start_buffer_zone  end_stop_id  \
2973348  801621     POLYGON ((7.157885983913106 50.7227...       1433.0   
3194413  801621     POLYGON ((7.157885983913106 50.7227...        701.0   
3041112  801621     POLYGON ((7.157885983913106 50.7227...       1102.0   
3075830  801621     POLYGON ((7.157885983913106 50.7227...       1115.0   
3211655  801621     POLYGON ((7.157885983913106 50.7227...       1502.0   
...                                                    ...          ...   
3482091  801621     POLYGON ((7.157885983913106 50.7227...       1102.0   
3482724  801621     POLYGON ((7.157885983913106 50.7227...       1115.0   
3410446  801621     POLYGON ((7.157885983913106 50.7227...       1442.0   
3305644  801621     POLYGON ((7.157885983913106 50.7227...       1135.0   
3376380  801621     POLYGON ((7.157885983913106 50.7227...       1131.0   

                                     end_stop_name  \
2973348                           Bonn Paulusplatz   
3194413                   Bonn Plittersdorfer Str.   
3041112                         Bonn Friedensplatz   
3075830  Bonn Bertha-Von-Suttner-Pl./Beethovenhaus   
3211655                 Bonn Beueler Bahnhofsplatz   
...                                            ...   
3482091                    

In [367]:
early_morning_no_delay_tier_station_station.describe()

tier_trips_id          tier_trips_start_time  \
count   1.110000e+02                            111   
mean    7.942870e+08  2023-07-13 23:26:45.405405696   
min     7.822657e+08            2023-07-01 04:35:00   
25%     7.823185e+08            2023-07-07 05:35:00   
50%     7.824274e+08            2023-07-12 04:55:00   
75%     8.087297e+08            2023-07-19 17:07:30   
max     8.322631e+08            2023-07-31 05:45:00   
std     1.576067e+07                            NaN   

                 tier_trips_end_time              trip_duration  \
count                            111                        111   
mean   2023-07-13 23:39:27.567567360  0 days 00:12:42.162162162   
min              2023-07-01 04:50:00            0 days 00:05:00   
25%              2023-07-07 05:47:30            0 days 00:10:00   
50%              2023-07-12 05:10:00            0 days 00:10:00   
75%              2023-07-19 17:22:30            0 days 00:15:00   
max              2023-07-31 05:55:00            0 days 01:15:00   
std                              NaN  0 days 00:08:31.335871482   

       trip_distance_kilometers  trip_distance_meters  start_stop_id  \
count                111.000000            111.000000     111.000000   
mean                   1.451054           1451.054280    1104.738739   
min                    0.104447            104.447092      43.000000   
25%                    0.647310            647.309785     687.000000   
50%                    1.073418           1073.418229    1106.000000   
75%                    2.162569           2162.568606    1184.000000   
max                    4.841966           4841.965856    9478.000000   
std                    1.054946           1054.946472     865.229930   

       end_stop_id  trip_duration_seconds  
count   111.000000             111.000000  
mean   1271.909910             762.162162  
min      43.000000             300.000000  
25%    1102.500000             600.000000  
50%    1131.000000             600.000000  
75%    1208.000000             900.000000  
max    8471.000000            4500.000000  
std    1052.798164             511.335871

In [368]:
# get statistics for the tier trips that start and end at a station
get_stats(early_morning_no_delay_tier_station_station, ['trip_duration_seconds', 'trip_distance_kilometers'])

column                                     trip_duration_seconds  \
rows                                                         111   
sum                                                      84600.0   
mean                                                  762.162162   
median                                                     600.0   
mode           0    600.0
Name: trip_duration_seconds, dtype:...   
max                                                       4500.0   
min                                                        300.0   
std_dev                                               511.335871   
variance                                           261464.373464   
skewness                                                4.057503   
kurtosis                                               25.688609   
percentile_25                                              600.0   
percentile_75                                              900.0   
iqr                                                        300.0   
range                                                     4200.0   
cv                                                      0.670902   
qd                                                           0.2   
cs                                                      0.007935   
ck                                                      0.050238   
cvs                                                     0.007935   
cvk                                                     0.050238   
cvcs                                                    0.007935   
cvck                                                    0.050238   
cvcv                                                    0.670902   
cvqd                                                         0.2   
cvr                                                     5.510638   
cvm                                                          1.0   
cvmed                                                   0.787234   
cvmode         0    0.787234
Name: trip_duration_seconds, dty...   

column                                  trip_distance_kilometers  
rows                                                         111  
sum                                                   161.067025  
mean                                                    1.451054  
median                                                  1.073418  
mode           0      0.104447
1      0.175968
2      0.17705...  
max                                                     4.841966  
min                                                     0.104447  
std_dev                                                 1.054946  
variance                                                1.112912  
skewness                                                1.137458  
kurtosis                                                0.985942  
percentile_25                                            0.64731  
percentile_75                                           2.162569  
iqr                                                     1.515259  
range                                                   4.737519  
cv                                                      0.727021  
qd                                                      0.539261  
cs                                                      1.078214  
ck                                                       0.93459  
cvs                                                     1.078214  
cvk                                                      0.93459  
cvcs                                                    1.078214  
cvck                                                     0.93459  
cvcv                                                    0.727021  
cvqd                                                    0.539261  
cvr                                                      3.26488  
cvm                                                          1.0  
cvmed                                                   0.739751  
cvmode         0

In [369]:
early_morning_no_delay_next = check_micromobility_datasets('next', early_morning_no_delay)

In [370]:
early_morning_no_delay_next.describe()

nextbike_trips_id      nextbike_trips_start_time  \
count       5.190000e+02                            519   
mean        3.794063e+07  2023-07-13 22:09:41.387283456   
min         3.771654e+07            2023-07-01 05:01:00   
25%         3.783113e+07            2023-07-06 05:56:00   
50%         3.794148e+07            2023-07-12 06:01:00   
75%         3.805072e+07            2023-07-20 05:26:00   
max         3.817075e+07            2023-07-31 06:01:00   
std         1.268538e+05                            NaN   

             nextbike_trips_end_time              trip_duration  \
count                            519                        519   
mean   2023-07-13 22:23:04.855491328  0 days 00:13:23.468208092   
min              2023-07-01 05:16:00            0 days 00:05:00   
25%              2023-07-06 06:11:00            0 days 00:10:00   
50%              2023-07-12 06:16:00            0 days 00:10:00   
75%              2023-07-20 05:36:00            0 days 00:15:00   
max              2023-07-31 06:11:00            0 days 01:20:00   
std                              NaN  0 days 00:07:40.262132012   

       trip_distance_kilometers  trip_distance_meters  start_stop_id  \
count                519.000000            519.000000     442.000000   
mean                   1.731785           1731.785190     995.201357   
min                    0.101501            101.500688      43.000000   
25%                    0.871756            871.755823     687.000000   
50%                    1.333014           1333.013935     688.000000   
75%                    2.332370           2332.369747    1153.000000   
max                   10.792084          10792.084377    8635.000000   
std                    1.306426           1306.425660     790.781122   

       end_stop_id  trip_duration_seconds  
count   292.000000             519.000000  
mean   1134.619863             803.468208  
min      43.000000             300.000000  
25%     687.000000             600.000000  
50%    1134.000000             600.000000  
75%    1221.000000             900.000000  
max    8813.000000            4800.000000  
std     792.342221             460.262132

In [371]:
get_stats(early_morning_no_delay_next, ['trip_duration_seconds', 'trip_distance_kilometers'])

column                                     trip_duration_seconds  \
rows                                                         519   
sum                                                     417000.0   
mean                                                  803.468208   
median                                                     600.0   
mode           0    600.0
Name: trip_duration_seconds, dtype:...   
max                                                       4800.0   
min                                                        300.0   
std_dev                                               460.262132   
variance                                           211841.230165   
skewness                                                4.003053   
kurtosis                                               27.559762   
percentile_25                                              600.0   
percentile_75                                              900.0   
iqr                                                        300.0   
range                                                     4500.0   
cv                                                      0.572844   
qd                                                           0.2   
cs                                                      0.008697   
ck                                                      0.059878   
cvs                                                     0.008697   
cvk                                                     0.059878   
cvcs                                                    0.008697   
cvck                                                    0.059878   
cvcv                                                    0.572844   
cvqd                                                         0.2   
cvr                                                     5.600719   
cvm                                                          1.0   
cvmed                                                   0.746763   
cvmode         0    0.746763
Name: trip_duration_seconds, dty...   

column                                  trip_distance_kilometers  
rows                                                         519  
sum                                                   898.796513  
mean                                                    1.731785  
median                                                  1.333014  
mode           0    0.46698
Name: trip_distance_kilometers, d...  
max                                                    10.792084  
min                                                     0.101501  
std_dev                                                 1.306426  
variance                                                1.706748  
skewness                                                1.885386  
kurtosis                                                6.254047  
percentile_25                                           0.871756  
percentile_75                                            2.33237  
iqr                                                     1.460614  
range                                                  10.690584  
cv                                                      0.754381  
qd                                                      0.455854  
cs                                                      1.443164  
ck                                                      4.787143  
cvs                                                     1.443164  
cvk                                                     4.787143  
cvcs                                                    1.443164  
cvck                                                    4.787143  
cvcv                                                    0.754381  
cvqd                                                    0.455854  
cvr                                                     6.173158  
cvm                                                          1.0  
cvmed                                                   0.769734  
cvmode         0

In [372]:
# get entries where trips start and end at station
early_morning_no_delay_next_station_station = early_morning_no_delay_next[early_morning_no_delay_next['end_stop_id'].notna() & early_morning_no_delay_next['start_stop_id'].notna()]
early_morning_no_delay_next_station_station

nextbike_trips_id nextbike_trips_start_time nextbike_trips_end_time  \
1444489           38015256       2023-07-01 05:31:00     2023-07-01 05:36:00   
1338605           37862861       2023-07-03 04:56:00     2023-07-03 05:11:00   
1665142           37796561       2023-07-03 05:16:00     2023-07-03 05:26:00   
1471548           38036106       2023-07-03 05:16:00     2023-07-03 05:31:00   
1486241           38047669       2023-07-03 05:31:00     2023-07-03 05:46:00   
...                    ...                       ...                     ...   
1594992           38134679       2023-07-31 05:21:00     2023-07-31 05:26:00   
1531634           38082649       2023-07-31 05:26:00     2023-07-31 05:41:00   
1626632           38160342       2023-07-31 05:26:00     2023-07-31 05:36:00   
1597005           37754646       2023-07-31 05:51:00     2023-07-31 05:56:00   
1290119           37839773       2023-07-31 06:01:00     2023-07-31 06:11:00   

         nextbike_trips_start_at_station  nextbike_trips_end_at_station  \
1444489                            False                           True   
1338605                            False                           True   
1665142                            False                          False   
1471548                            False                          False   
1486241                            False                          False   
...                                  ...                            ...   
1594992                            False                          False   
1531634                            False                          False   
1626632                            False                          False   
1597005                             True                          False   
1290119                            False                          False   

        vehicle type   trip_duration  trip_distance_kilometers  \
1444489         bike 0 days 00:05:00                  0.109052   
1338605         bike 0 days 00:15:00                  2.516433   
1665142         bike 0 days 00:10:00                  0.743004   
1471548         bike 0 days 00:15:00                  3.080515   
1486241         bike 0 days 00:15:00                  2.152018   
...              ...             ...                       ...   
1594992         bike 0 days 00:05:00                  0.132695   
1531634         bike 0 days 00:15:00                  1.611584   
1626632         bike 0 days 00:10:00                  0.941277   
1597005         bike 0 days 00:05:00                  0.809998   
1290119         bike 0 days 00:10:00                  1.936608   

         trip_distance_meters  \
1444489            109.052108   
1338605           2516.433094   
1665142            743.004477   
1471548           3080.515217   
1486241           2152.018454   
...                       ...   
1594992            132.695234   
1531634           1611.584349   
1626632            941.276815   
1597005            809.997652   
1290119           1936.608429   

                                            start_location  \
1444489  b'\x01\x01\x00\x00\x00\x0c@\xa3t\xe9/\x1c@\x1c...   
1338605  b'\x01\x01\x00\x00\x00X\xfe|[\xb0d\x1c@\xef\x0...   
1665142  b'\x01\x01\x00\x00\x00\x00<\xa2Buc\x1c@\x99\r2...   
1471548  b'\x01\x01\x00\x00\x00\xf5*2: i\x1c@F\xce\xc2\...   
1486241  b'\x01\x01\x00\x00\x00\x91}\x90e\xc1d\x1c@D\xd...   
...                                                    ...   
1594992  b'\x01\x01\x00\x00\x00\x89x\xeb\xfc\xdbe\x1c@\...   
1531634  b'\x01\x01\x00\x00\x00\xd7\xa6\xb1\xbd\x16d\x1...   
1626632  b'\x01\x01\x00\x00\x00\x82\xfd\xd7\xb9ic\x1c@\...   
1597005  b'\x01\x01\x00\x00\x00&\x199\x0b{Z\x1c@\xb4\xe...   
1290119  b'\x01\x01\x00\x00\x00\xae\xd7\xf4\xa0\xa0d\x1...   

                                              end_location  start_stop_id  \
1444489  b'\x01\x01\x00\x00\x00W\xb2c#\x10/\x1c@ap\xcd\...          694.0   
1338605  b'\x01\x01\x00\x00\x007m\xc6i\x88z\x1c@\xb0\xf...

In [373]:
early_morning_no_delay_next_station_station.describe()

nextbike_trips_id      nextbike_trips_start_time  \
count       2.480000e+02                            248   
mean        3.795076e+07  2023-07-13 08:03:25.161290496   
min         3.772054e+07            2023-07-01 05:31:00   
25%         3.784985e+07            2023-07-06 05:44:45   
50%         3.795448e+07            2023-07-12 05:48:30   
75%         3.805671e+07            2023-07-19 05:28:30   
max         3.817075e+07            2023-07-31 06:01:00   
std         1.243095e+05                            NaN   

             nextbike_trips_end_time              trip_duration  \
count                            248                        248   
mean   2023-07-13 08:15:44.274193408  0 days 00:12:19.112903225   
min              2023-07-01 05:36:00            0 days 00:05:00   
25%              2023-07-06 06:01:00            0 days 00:10:00   
50%              2023-07-12 06:01:00            0 days 00:10:00   
75%              2023-07-19 05:38:30            0 days 00:15:00   
max              2023-07-31 06:11:00            0 days 01:05:00   
std                              NaN  0 days 00:06:03.020419891   

       trip_distance_kilometers  trip_distance_meters  start_stop_id  \
count                248.000000            248.000000     248.000000   
mean                   1.448283           1448.282834    1006.600806   
min                    0.101501            101.500688      43.000000   
25%                    0.765505            765.505455     687.000000   
50%                    1.163383           1163.382740     693.500000   
75%                    1.879419           1879.419392    1160.000000   
max                    6.369120           6369.119647    8506.000000   
std                    1.059925           1059.925214     739.431003   

       end_stop_id  trip_duration_seconds  
count   248.000000             248.000000  
mean   1151.758065             739.112903  
min      43.000000             300.000000  
25%     691.250000             600.000000  
50%    1132.500000             600.000000  
75%    1221.000000             900.000000  
max    8813.000000            3900.000000  
std     846.482800             363.020420

In [374]:
# get statistics for the tier trips that start and end at a station
get_stats(early_morning_no_delay_next_station_station, ['trip_duration_seconds', 'trip_distance_kilometers'])

column                                     trip_duration_seconds  \
rows                                                         248   
sum                                                     183300.0   
mean                                                  739.112903   
median                                                     600.0   
mode           0    600.0
Name: trip_duration_seconds, dtype:...   
max                                                       3900.0   
min                                                        300.0   
std_dev                                                363.02042   
variance                                           131783.825258   
skewness                                                 3.11236   
kurtosis                                               22.498888   
percentile_25                                              600.0   
percentile_75                                              900.0   
iqr                                                        300.0   
range                                                     3600.0   
cv                                                      0.491157   
qd                                                           0.2   
cs                                                      0.008574   
ck                                                      0.061977   
cvs                                                     0.008574   
cvk                                                     0.061977   
cvcs                                                    0.008574   
cvck                                                    0.061977   
cvcv                                                    0.491157   
cvqd                                                         0.2   
cvr                                                     4.870704   
cvm                                                          1.0   
cvmed                                                   0.811784   
cvmode         0    0.811784
Name: trip_duration_seconds, dty...   

column                                  trip_distance_kilometers  
rows                                                         248  
sum                                                   359.174143  
mean                                                    1.448283  
median                                                  1.163383  
mode           0    0.98257
Name: trip_distance_kilometers, d...  
max                                                      6.36912  
min                                                     0.101501  
std_dev                                                 1.059925  
variance                                                1.123441  
skewness                                                1.708716  
kurtosis                                                 3.59645  
percentile_25                                           0.765505  
percentile_75                                           1.879419  
iqr                                                     1.113914  
range                                                   6.267619  
cv                                                       0.73185  
qd                                                      0.421151  
cs                                                       1.61211  
ck                                                      3.393117  
cvs                                                      1.61211  
cvk                                                     3.393117  
cvcs                                                     1.61211  
cvck                                                    3.393117  
cvcv                                                     0.73185  
cvqd                                                    0.421151  
cvr                                                     4.327621  
cvm                                                          1.0  
cvmed                                                   0.803284  
cvmode         0

In [375]:
early_morning_nan_delay = nan_delay[(nan_delay['scheduled_arrival_time'].dt.hour > 2) & (nan_delay['scheduled_arrival_time'].dt.hour < 6)]
early_morning_nan_delay

route_id  agency_id route_short_name  route_type route_type_name  \
41            551          8              551           3             Bus   
42            551          8              551           3             Bus   
43            551          8              551           3             Bus   
44            551          8              551           3             Bus   
45            551          8              551           3             Bus   
...           ...        ...              ...         ...             ...   
2564854       689          6               N9           3             Bus   
2564856       689          6               N9           3             Bus   
2564857       689          6               N9           3             Bus   
2564858       689          6               N9           3             Bus   
2564860       689          6               N9           3             Bus   

                                      agency_name  service_id  \
41       RSVG Rhein-Sieg-Verkehrsgesellschaft mbH         125   
42       RSVG Rhein-Sieg-Verkehrsgesellschaft mbH         125   
43       RSVG Rhein-Sieg-Verkehrsgesellschaft mbH         125   
44       RSVG Rhein-Sieg-Verkehrsgesellschaft mbH         125   
45       RSVG Rhein-Sieg-Verkehrsgesellschaft mbH         125   
...                                           ...         ...   
2564854         SWB Stadtwerke Bonn Verkehrs GmbH          43   
2564856         SWB Stadtwerke Bonn Verkehrs GmbH          43   
2564857         SWB Stadtwerke Bonn Verkehrs GmbH          43   
2564858         SWB Stadtwerke Bonn Verkehrs GmbH          43   
2564860         SWB Stadtwerke Bonn Verkehrs GmbH          43   

                                                   trip_id trip_headsign  \
41       255-551-008-2071.2.22:033200-34-157_C0741D60-B...      Bonn Hbf   
42       159-551-008-687.2.36:044000-33-157_FAA787CB-18...  Troisdorf Bf   
43       159-551-008-687.2.36:044000-33-157_FAA787CB-18...  Troisdorf Bf   
44       159-551-008-687.2.36:044000-33-157_FAA787CB-18...  Troisdorf Bf   
45       159-551-008-687.2.36:044000-33-157_FAA787CB-18...  Troisdorf Bf   
...                                                    ...           ...   
2564854  6890005-689-006-687.2.34:263500-53-1_2AFE8F0F-...      Bonn Hbf   
2564856  6890005-689-006-687.2.34:263500-53-1_2AFE8F0F-...      Bonn Hbf   
2564857  6890005-689-006-687.2.34:263500-53-1_2AFE8F0F-...      Bonn Hbf   
2564858  6890005-689-006-687.2.34:263500-53-1_2AFE8F0F-...      Bonn Hbf   
2564860  6890005-689-006-687.2.34:263500-53-1_2AFE8F0F-...      Bonn Hbf   

         direction_id  ...  delay_span  arrival_delay_span weather_int  \
41                  1  ...           0                   0           0   
42                  0  ...           0                   0           0   
43                  0  ...           0                   0           0   
44                  0  ...           0                   0           0   
45                  0  ...           0                   0           0   
...               ...  ...         ...                 ...         ...   
2564854             0  ...           0                   0           1   
2564856             0  ...           0                   0           1   
2564857             0  ...           0                   0           1   
2564858             0  ...           0                   0           1   
2564860             0  ...           0                   0           1   

        time_span_arrival  time_span_int_arrival  weekend time_span  \
41                      0                      0        1         0   
42                      0                      0        1         0   
43                      0                      0        1         0   
44                      0                      0        1         0   
45                      0                      0        1         0   
...                   ...                    ...      ...       ...   
2564

In [376]:
get_stats(early_morning_nan_delay, ['tier_trips_count', 'tier_trips_end_at_station_count', 'nextbike_trips_count', 'nextbike_trips_end_at_station_count', 'current_temp', 'current_precipitation_volume'])

/tmp/ipykernel_2575952/41814695.py:51: RuntimeWarning: invalid value encountered in scalar divide
  qd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:55: RuntimeWarning: invalid value encountered in scalar divide
  cvqd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:51: RuntimeWarning: invalid value encountered in scalar divide
  qd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:55: RuntimeWarning: invalid value encountered in scalar divide
  cvqd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:51: RuntimeWarning: invalid value encountered in scalar divide
  qd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:55: RuntimeWarning: invalid value encountered in scalar divide
  cvqd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:51: RuntimeWarning: invalid value encountered in scalar divide
  qd = iqr / (percentile_75 + percenti

column                                        tier_trips_count  \
rows                                                     31305   
sum                                                        357   
mean                                                  0.011404   
median                                                     0.0   
mode               0    0
Name: tier_trips_count, dtype: int64   
max                                                          2   
min                                                          0   
std_dev                                               0.107377   
variance                                               0.01153   
skewness                                               9.51168   
kurtosis                                             92.154248   
percentile_25                                              0.0   
percentile_75                                              0.0   
iqr                                                        0.0   
range                                                        2   
cv                                                    9.415781   
qd                                                         NaN   
cs                                                   88.582185   
ck                                                  858.231616   
cvs                                                  88.582185   
cvk                                                 858.231616   
cvcs                                                 88.582185   
cvck                                                858.231616   
cvcv                                                  9.415781   
cvqd                                                       NaN   
cvr                                                 175.378151   
cvm                                                        1.0   
cvmed                                                      0.0   
cvmode         0    0.0
Name: tier_trips_count, dtype: float64   

column                           tier_trips_end_at_station_count  \
rows                                                       31305   
sum                                                          313   
mean                                                    0.009998   
median                                                       0.0   
mode           0    0
Name: tier_trips_end_at_station_count, ...   
max                                                            2   
min                                                            0   
std_dev                                                 0.100769   
variance                                                0.010154   
skewness                                                10.22295   
kurtosis                                              107.225518   
percentile_25                                                0.0   
percentile_75                                                0.0   
iqr                                                          0.0   
range                                                          2   
cv                                                     10.078469   
qd                                                           NaN   
cs                                                    101.449769   
ck                                                   1064.076762   
cvs                                                   101.449769   
cvk                                                  1064.076762   
cvcs                                                  101.449769   
cvck                                                 1064.076762   
cvcv                                                   10.078469   
cvqd                                                         NaN   
cvr                                                   200.031949   
cvm                                                          1.0   
cvmed                                                        0.0   
cvmode         0    0.0
Name: tier_trips_end_at

In [377]:
early_morning_nan_delay_tier = check_micromobility_datasets('tier', early_morning_nan_delay)

In [378]:
early_morning_nan_delay_tier.describe()

tier_trips_id          tier_trips_start_time  \
count   2.170000e+02                            217   
mean    7.950504e+08  2023-07-14 07:34:29.585253376   
min     7.822652e+08            2023-07-01 04:35:00   
25%     7.823438e+08            2023-07-07 05:30:00   
50%     7.824324e+08            2023-07-12 05:40:00   
75%     8.087302e+08            2023-07-21 04:50:00   
max     8.323071e+08            2023-07-31 05:45:00   
std     1.581834e+07                            NaN   

                 tier_trips_end_time              trip_duration  \
count                            217                        217   
mean   2023-07-14 07:48:17.695852544  0 days 00:13:48.110599078   
min              2023-07-01 04:50:00            0 days 00:05:00   
25%              2023-07-07 05:40:00            0 days 00:10:00   
50%              2023-07-12 05:50:00            0 days 00:10:00   
75%              2023-07-21 05:00:00            0 days 00:15:00   
max              2023-07-31 05:55:00            0 days 01:15:00   
std                              NaN  0 days 00:07:54.139207101   

       trip_distance_kilometers  trip_distance_meters  start_stop_id  \
count                217.000000            217.000000     169.000000   
mean                   1.797703           1797.702563    1149.928994   
min                    0.117351            117.351249     161.000000   
25%                    0.811951            811.951013     687.000000   
50%                    1.532172           1532.171923    1115.000000   
75%                    2.282908           2282.908216    1231.000000   
max                    7.547788           7547.787527    8506.000000   
std                    1.377539           1377.539148     894.309135   

       end_stop_id  trip_duration_seconds  
count   138.000000             217.000000  
mean   1330.905797             828.110599  
min      43.000000             300.000000  
25%     687.250000             600.000000  
50%    1115.000000             600.000000  
75%    1222.500000             900.000000  
max    9073.000000            4500.000000  
std    1466.089151             474.139207

In [379]:
get_stats(early_morning_nan_delay_tier, ['trip_duration_seconds', 'trip_distance_kilometers'])

column                                     trip_duration_seconds  \
rows                                                         217   
sum                                                     179700.0   
mean                                                  828.110599   
median                                                     600.0   
mode           0    600.0
Name: trip_duration_seconds, dtype:...   
max                                                       4500.0   
min                                                        300.0   
std_dev                                               474.139207   
variance                                           224807.987711   
skewness                                                3.156556   
kurtosis                                                18.10082   
percentile_25                                              600.0   
percentile_75                                              900.0   
iqr                                                        300.0   
range                                                     4200.0   
cv                                                      0.572555   
qd                                                           0.2   
cs                                                      0.006657   
ck                                                      0.038176   
cvs                                                     0.006657   
cvk                                                     0.038176   
cvcs                                                    0.006657   
cvck                                                    0.038176   
cvcv                                                    0.572555   
cvqd                                                         0.2   
cvr                                                     5.071786   
cvm                                                          1.0   
cvmed                                                   0.724541   
cvmode         0    0.724541
Name: trip_duration_seconds, dty...   

column                                  trip_distance_kilometers  
rows                                                         217  
sum                                                   390.101456  
mean                                                    1.797703  
median                                                  1.532172  
mode           0      0.117351
1      0.142476
2      0.15076...  
max                                                     7.547788  
min                                                     0.117351  
std_dev                                                 1.377539  
variance                                                1.897614  
skewness                                                1.753006  
kurtosis                                                3.761254  
percentile_25                                           0.811951  
percentile_75                                           2.282908  
iqr                                                     1.470957  
range                                                   7.430436  
cv                                                      0.766278  
qd                                                      0.475291  
cs                                                      1.272564  
ck                                                      2.730415  
cvs                                                     1.272564  
cvk                                                     2.730415  
cvcs                                                    1.272564  
cvck                                                    2.730415  
cvcv                                                    0.766278  
cvqd                                                    0.475291  
cvr                                                     4.133296  
cvm                                                          1.0  
cvmed                                                   0.852294  
cvmode         0

In [380]:
# get entries where trips start and end at station
early_morning_nan_delay_tier_station_station = early_morning_nan_delay_tier[early_morning_nan_delay_tier['end_stop_id'].notna() & early_morning_nan_delay_tier['start_stop_id'].notna()]
early_morning_nan_delay_tier_station_station

tier_trips_id tier_trips_start_time tier_trips_end_time vehicle type  \
2973348      782286043   2023-07-01 04:35:00 2023-07-01 04:50:00    e-scooter   
3254646      782432382   2023-07-01 05:35:00 2023-07-01 06:05:00    e-scooter   
3044065      782307646   2023-07-01 05:40:00 2023-07-01 05:50:00    e-scooter   
3041112      782306453   2023-07-02 05:50:00 2023-07-02 06:00:00    e-scooter   
3211655      782393209   2023-07-04 05:15:00 2023-07-04 05:25:00    e-scooter   
...                ...                   ...                 ...          ...   
3524687      832303304   2023-07-29 05:35:00 2023-07-29 05:45:00    e-scooter   
3517663      832296583   2023-07-29 06:00:00 2023-07-29 06:10:00    e-scooter   
3481497      832261873   2023-07-30 05:45:00 2023-07-30 05:55:00    e-scooter   
3305644      832111334   2023-07-31 05:30:00 2023-07-31 05:40:00    e-scooter   
3376380      832161003   2023-07-31 05:45:00 2023-07-31 05:55:00    e-scooter   

          trip_duration  trip_distance_kilometers  trip_distance_meters  \
2973348 0 days 00:15:00                  3.658388           3658.388003   
3254646 0 days 00:30:00                  6.647158           6647.158439   
3044065 0 days 00:10:00                  1.031855           1031.854950   
3041112 0 days 00:10:00                  2.363298           2363.298081   
3211655 0 days 00:10:00                  0.908268            908.267654   
...                 ...                       ...                   ...   
3524687 0 days 00:10:00                  0.682744            682.744130   
3517663 0 days 00:10:00                  1.216502           1216.502368   
3481497 0 days 00:10:00                  1.958646           1958.646446   
3305644 0 days 00:10:00                  0.741660            741.659744   
3376380 0 days 00:10:00                  0.999367            999.366812   

         start_stop_id                            start_stop_name  \
2973348          687.0                                   Bonn Hbf   
3254646         2516.0                         Bonn Im Erlenbusch   
3044065          689.0                          Bonn Brühler Str.   
3041112         1500.0                 Bonn Konrad-Adenauer-Platz   
3211655         1500.0                 Bonn Konrad-Adenauer-Platz   
...                ...                                        ...   
3524687         1115.0  Bonn Bertha-Von-Suttner-Pl./Beethovenhaus   
3517663         1161.0                          Bonn An Der Esche   
3481497          686.0                     Bonn Universität/Markt   
3305644          687.0                                   Bonn Hbf   
3376380          687.0                                   Bonn Hbf   

                                         start_buffer_zone  end_stop_id  \
2973348  801621     POLYGON ((7.157885983913106 50.7227...       1433.0   
3254646  801621     POLYGON ((7.157885983913106 50.7227...       1500.0   
3044065  801621     POLYGON ((7.157885983913106 50.7227...       1404.0   
3041112  801621     POLYGON ((7.157885983913106 50.7227...       1102.0   
3211655  801621     POLYGON ((7.157885983913106 50.7227...       1502.0   
...                                                    ...          ...   
3524687  801621     POLYGON ((7.157885983913106 50.7227...        686.0   
3517663  801621     POLYGON ((7.157885983913106 50.7227...        687.0   
3481497  801621     POLYGON ((7.157885983913106 50.7227...       1500.0   
3305644  801621     POLYGON ((7.157885983913106 50.7227...       1135.0   
3376380  801621     POLYGON ((7.157885983913106 50.7227...       1131.0   

                         end_stop_name  \
2973348               Bonn Paulusplatz   
3254646     Bonn Konrad-Adenauer-Platz   
3044065     Bonn Friedrich-Wöhler-Str.   
3041112             Bonn Friedensplatz   
3211655     Bonn Beueler Bahnhofsplatz   
...                                ...   
3524687         Bonn Universität/Markt   
3517663                       Bonn Hbf   
3481497     Bonn Konrad-Ade

In [381]:
early_morning_nan_delay_tier_station_station.describe()

tier_trips_id          tier_trips_start_time  \
count   1.170000e+02                            117   
mean    7.946049e+08  2023-07-14 09:09:21.538461440   
min     7.822654e+08            2023-07-01 04:35:00   
25%     7.823438e+08            2023-07-07 05:30:00   
50%     7.824319e+08            2023-07-12 05:30:00   
75%     8.087177e+08            2023-07-21 05:35:00   
max     8.323033e+08            2023-07-31 05:45:00   
std     1.533417e+07                            NaN   

                 tier_trips_end_time              trip_duration  \
count                            117                        117   
mean   2023-07-14 09:22:33.846153728  0 days 00:13:12.307692307   
min              2023-07-01 04:50:00            0 days 00:05:00   
25%              2023-07-07 05:35:00            0 days 00:10:00   
50%              2023-07-12 05:40:00            0 days 00:10:00   
75%              2023-07-21 05:50:00            0 days 00:15:00   
max              2023-07-31 05:55:00            0 days 01:15:00   
std                              NaN  0 days 00:08:12.732326815   

       trip_distance_kilometers  trip_distance_meters  start_stop_id  \
count                117.000000            117.000000     117.000000   
mean                   1.494118           1494.117528    1199.452991   
min                    0.189906            189.905629     371.000000   
25%                    0.783018            783.018280     687.000000   
50%                    1.198196           1198.195991    1110.000000   
75%                    1.858566           1858.565527    1184.000000   
max                    7.461071           7461.071462    8506.000000   
std                    1.112788           1112.787686    1039.424182   

       end_stop_id  trip_duration_seconds  
count   117.000000             117.000000  
mean   1352.230769             792.307692  
min      43.000000             300.000000  
25%     690.000000             600.000000  
50%    1131.000000             600.000000  
75%    1224.000000             900.000000  
max    9073.000000            4500.000000  
std    1457.328167             492.732327

In [382]:
# get statistics for the tier trips that start and end at a station
get_stats(early_morning_nan_delay_tier_station_station, ['trip_duration_seconds', 'trip_distance_kilometers'])

column                                     trip_duration_seconds  \
rows                                                         117   
sum                                                      92700.0   
mean                                                  792.307692   
median                                                     600.0   
mode           0    600.0
Name: trip_duration_seconds, dtype:...   
max                                                       4500.0   
min                                                        300.0   
std_dev                                               492.732327   
variance                                           242785.145889   
skewness                                                4.110295   
kurtosis                                               27.362364   
percentile_25                                              600.0   
percentile_75                                              900.0   
iqr                                                        300.0   
range                                                     4200.0   
cv                                                      0.621895   
qd                                                           0.2   
cs                                                      0.008342   
ck                                                      0.055532   
cvs                                                     0.008342   
cvk                                                     0.055532   
cvcs                                                    0.008342   
cvck                                                    0.055532   
cvcv                                                    0.621895   
cvqd                                                         0.2   
cvr                                                     5.300971   
cvm                                                          1.0   
cvmed                                                   0.757282   
cvmode         0    0.757282
Name: trip_duration_seconds, dty...   

column                                  trip_distance_kilometers  
rows                                                         117  
sum                                                   174.811751  
mean                                                    1.494118  
median                                                  1.198196  
mode           0      0.189906
1      0.190209
2      0.20336...  
max                                                     7.461071  
min                                                     0.189906  
std_dev                                                 1.112788  
variance                                                1.238296  
skewness                                                2.558588  
kurtosis                                                9.998091  
percentile_25                                           0.783018  
percentile_75                                           1.858566  
iqr                                                     1.075547  
range                                                   7.271166  
cv                                                      0.744779  
qd                                                       0.40716  
cs                                                       2.29926  
ck                                                      8.984725  
cvs                                                      2.29926  
cvk                                                     8.984725  
cvcs                                                     2.29926  
cvck                                                    8.984725  
cvcv                                                    0.744779  
cvqd                                                     0.40716  
cvr                                                     4.866529  
cvm                                                          1.0  
cvmed                                                   0.801942  
cvmode         0

In [383]:
early_morning_nan_delay_next = check_micromobility_datasets('next', early_morning_nan_delay)

In [384]:
early_morning_nan_delay_next.describe()

nextbike_trips_id      nextbike_trips_start_time  \
count       6.870000e+02                            687   
mean        3.794147e+07  2023-07-14 19:45:28.995633152   
min         3.771654e+07            2023-07-01 05:16:00   
25%         3.783138e+07            2023-07-07 05:31:00   
50%         3.794772e+07            2023-07-13 05:36:00   
75%         3.805091e+07            2023-07-21 05:46:00   
max         3.817038e+07            2023-08-01 03:21:00   
std         1.269073e+05                            NaN   

             nextbike_trips_end_time              trip_duration  \
count                            687                        687   
mean   2023-07-14 19:59:05.152838400  0 days 00:13:36.157205240   
min              2023-07-01 05:26:00            0 days 00:05:00   
25%              2023-07-07 05:48:30            0 days 00:10:00   
50%              2023-07-13 05:46:00            0 days 00:10:00   
75%              2023-07-21 05:56:00            0 days 00:15:00   
max              2023-08-01 03:31:00            0 days 02:00:00   
std                              NaN  0 days 00:07:38.497125110   

       trip_distance_kilometers  trip_distance_meters  start_stop_id  \
count                687.000000            687.000000     549.000000   
mean                   1.776409           1776.409190    1219.717668   
min                    0.101501            101.500688     161.000000   
25%                    0.899232            899.232329     687.000000   
50%                    1.420950           1420.950032    1115.000000   
75%                    2.404974           2404.973968    1223.000000   
max                    8.889750           8889.750492    9780.000000   
std                    1.301828           1301.828310    1313.106746   

       end_stop_id  trip_duration_seconds  
count   417.000000             687.000000  
mean   1120.266187             816.157205  
min      43.000000             300.000000  
25%     687.000000             600.000000  
50%    1115.000000             600.000000  
75%    1221.000000             900.000000  
max    9039.000000            7200.000000  
std    1027.358000             458.497125

In [385]:
get_stats(early_morning_nan_delay_next, ['trip_duration_seconds', 'trip_distance_kilometers'])

column                                     trip_duration_seconds  \
rows                                                         687   
sum                                                     560700.0   
mean                                                  816.157205   
median                                                     600.0   
mode           0    600.0
Name: trip_duration_seconds, dtype:...   
max                                                       7200.0   
min                                                        300.0   
std_dev                                               458.497125   
variance                                           210219.613734   
skewness                                                5.220174   
kurtosis                                               59.082579   
percentile_25                                              600.0   
percentile_75                                              900.0   
iqr                                                        300.0   
range                                                     6900.0   
cv                                                      0.561776   
qd                                                           0.2   
cs                                                      0.011385   
ck                                                      0.128861   
cvs                                                     0.011385   
cvk                                                     0.128861   
cvcs                                                    0.011385   
cvck                                                    0.128861   
cvcv                                                    0.561776   
cvqd                                                         0.2   
cvr                                                     8.454254   
cvm                                                          1.0   
cvmed                                                   0.735152   
cvmode         0    0.735152
Name: trip_duration_seconds, dty...   

column                                  trip_distance_kilometers  
rows                                                         687  
sum                                                  1220.393114  
mean                                                    1.776409  
median                                                   1.42095  
mode           0    0.46698
Name: trip_distance_kilometers, d...  
max                                                      8.88975  
min                                                     0.101501  
std_dev                                                 1.301828  
variance                                                1.694757  
skewness                                                 1.48326  
kurtosis                                                2.782043  
percentile_25                                           0.899232  
percentile_75                                           2.404974  
iqr                                                     1.505742  
range                                                    8.78825  
cv                                                      0.732843  
qd                                                      0.455704  
cs                                                      1.139367  
ck                                                      2.137028  
cvs                                                     1.139367  
cvk                                                     2.137028  
cvcs                                                    1.139367  
cvck                                                    2.137028  
cvcv                                                    0.732843  
cvqd                                                    0.455704  
cvr                                                     4.947199  
cvm                                                          1.0  
cvmed                                                     0.7999  
cvmode         0

In [386]:
# get entries where trips start and end at station
early_morning_nan_delay_next_station_station = early_morning_nan_delay_next[early_morning_nan_delay_next['end_stop_id'].notna() & early_morning_nan_delay_next['start_stop_id'].notna()]
early_morning_nan_delay_next_station_station

nextbike_trips_id nextbike_trips_start_time nextbike_trips_end_time  \
1635116           37766535       2023-07-01 05:16:00     2023-07-01 05:26:00   
1444489           38015256       2023-07-01 05:31:00     2023-07-01 05:36:00   
1665142           37796561       2023-07-03 05:16:00     2023-07-03 05:26:00   
1570657           38117565       2023-07-03 05:21:00     2023-07-03 05:31:00   
1486241           38047669       2023-07-03 05:31:00     2023-07-03 05:46:00   
...                    ...                       ...                     ...   
1235412           37726080       2023-07-31 05:36:00     2023-07-31 05:56:00   
1641660           37773079       2023-07-31 05:41:00     2023-07-31 05:46:00   
1375584           37940782       2023-07-31 05:41:00     2023-07-31 05:56:00   
1439945           37969647       2023-07-31 05:46:00     2023-07-31 06:06:00   
1404562           37955702       2023-08-01 03:21:00     2023-08-01 03:31:00   

         nextbike_trips_start_at_station  nextbike_trips_end_at_station  \
1635116                            False                           True   
1444489                            False                           True   
1665142                            False                          False   
1570657                            False                          False   
1486241                            False                          False   
...                                  ...                            ...   
1235412                            False                          False   
1641660                            False                           True   
1375584                            False                          False   
1439945                            False                          False   
1404562                            False                          False   

        vehicle type   trip_duration  trip_distance_kilometers  \
1635116         bike 0 days 00:10:00                  1.003667   
1444489         bike 0 days 00:05:00                  0.109052   
1665142         bike 0 days 00:10:00                  0.743004   
1570657         bike 0 days 00:10:00                  1.417101   
1486241         bike 0 days 00:15:00                  2.152018   
...              ...             ...                       ...   
1235412         bike 0 days 00:20:00                  3.126230   
1641660         bike 0 days 00:05:00                  0.406897   
1375584         bike 0 days 00:15:00                  1.467484   
1439945         bike 0 days 00:20:00                  4.354365   
1404562         bike 0 days 00:10:00                  0.996805   

         trip_distance_meters  \
1635116           1003.666723   
1444489            109.052108   
1665142            743.004477   
1570657           1417.100838   
1486241           2152.018454   
...                       ...   
1235412           3126.229873   
1641660            406.896701   
1375584           1467.483771   
1439945           4354.364505   
1404562            996.805000   

                                            start_location  \
1635116  b"\x01\x01\x00\x00\x00Z\xb7A\xed\xb7\x96\x1c@L...   
1444489  b'\x01\x01\x00\x00\x00\x0c@\xa3t\xe9/\x1c@\x1c...   
1665142  b'\x01\x01\x00\x00\x00\x00<\xa2Buc\x1c@\x99\r2...   
1570657  b'\x01\x01\x00\x00\x00`YiR\nZ\x1c@\xdb\xfa\xe9...   
1486241  b'\x01\x01\x00\x00\x00\x91}\x90e\xc1d\x1c@D\xd...   
...                                                    ...   
1235412  b'\x01\x01\x00\x00\x00Uj\xf6@+P\x1c@G\xb0q\xfd...   
1641660  b'\x01\x01\x00\x00\x00\xf9\x11\xbfb\rg\x1c@\xe...   
1375584  b"\x01\x01\x00\x00\x00iq\xc60'h\x1c@\xd7\x18tB...   
1439945  b'\x01\x01\x00\x00\x00S\xb0\xc6\xd9td\x1c@\xc5...   
1404562  b'\x01\x01\x00\x00\x00\x08v\xfc\x17\x08b\x1c@\...   

                                              end_location  start_stop_id  \
1635116  b'\x01\x01\x00\x00\x00t\xef\xe1\x92\xe3\x9e\x1...         8950.0   
1444489  b'\x01\x01\x00\x00\x00W\xb2c#\x10/\x1c@ap\xcd\...

In [387]:
early_morning_nan_delay_next_station_station.describe()

nextbike_trips_id      nextbike_trips_start_time  \
count       3.400000e+02                            340   
mean        3.793645e+07  2023-07-14 12:08:28.235294208   
min         3.771675e+07            2023-07-01 05:16:00   
25%         3.782755e+07            2023-07-06 23:12:15   
50%         3.793809e+07            2023-07-12 06:01:00   
75%         3.804610e+07            2023-07-20 11:52:15   
max         3.816837e+07            2023-08-01 03:21:00   
std         1.250909e+05                            NaN   

             nextbike_trips_end_time              trip_duration  \
count                            340                        340   
mean   2023-07-14 12:21:04.411764992  0 days 00:12:36.176470588   
min              2023-07-01 05:26:00            0 days 00:05:00   
25%              2023-07-06 23:26:00            0 days 00:10:00   
50%              2023-07-12 06:13:30            0 days 00:10:00   
75%              2023-07-20 12:06:00            0 days 00:15:00   
max              2023-08-01 03:31:00            0 days 02:00:00   
std                              NaN  0 days 00:08:19.784701173   

       trip_distance_kilometers  trip_distance_meters  start_stop_id  \
count                340.000000            340.000000     340.000000   
mean                   1.433151           1433.150501    1360.208824   
min                    0.101501            101.500688     161.000000   
25%                    0.760718            760.718231     687.000000   
50%                    1.220781           1220.780610    1140.000000   
75%                    1.699527           1699.526943    1235.000000   
max                    6.369120           6369.119647    9780.000000   
std                    1.056098           1056.098291    1573.199740   

       end_stop_id  trip_duration_seconds  
count   340.000000             340.000000  
mean   1170.844118             756.176471  
min      43.000000             300.000000  
25%     687.000000             600.000000  
50%    1115.000000             600.000000  
75%    1221.000000             900.000000  
max    9039.000000            7200.000000  
std    1121.065779             499.784701

In [388]:
# get statistics for the tier trips that start and end at a station
get_stats(early_morning_nan_delay_next_station_station, ['trip_duration_seconds', 'trip_distance_kilometers'])

column                                     trip_duration_seconds  \
rows                                                         340   
sum                                                     257100.0   
mean                                                  756.176471   
median                                                     600.0   
mode           0    600.0
Name: trip_duration_seconds, dtype:...   
max                                                       7200.0   
min                                                        300.0   
std_dev                                               499.784701   
variance                                           249784.747527   
skewness                                                7.330029   
kurtosis                                               85.508303   
percentile_25                                              600.0   
percentile_75                                              900.0   
iqr                                                        300.0   
range                                                     6900.0   
cv                                                      0.660937   
qd                                                           0.2   
cs                                                      0.014666   
ck                                                       0.17109   
cvs                                                     0.014666   
cvk                                                      0.17109   
cvcs                                                    0.014666   
cvck                                                     0.17109   
cvcv                                                    0.660937   
cvqd                                                         0.2   
cvr                                                     9.124854   
cvm                                                          1.0   
cvmed                                                   0.793466   
cvmode         0    0.793466
Name: trip_duration_seconds, dty...   

column                                  trip_distance_kilometers  
rows                                                         340  
sum                                                    487.27117  
mean                                                    1.433151  
median                                                  1.220781  
mode           0    0.982570
1    1.482255
Name: trip_distanc...  
max                                                      6.36912  
min                                                     0.101501  
std_dev                                                 1.056098  
variance                                                1.115344  
skewness                                                1.844505  
kurtosis                                                4.260477  
percentile_25                                           0.760718  
percentile_75                                           1.699527  
iqr                                                     0.938809  
range                                                   6.267619  
cv                                                      0.736907  
qd                                                      0.381592  
cs                                                      1.746528  
ck                                                      4.034167  
cvs                                                     1.746528  
cvk                                                     4.034167  
cvcs                                                    1.746528  
cvck                                                    4.034167  
cvcv                                                    0.736907  
cvqd                                                    0.381592  
cvr                                                     4.373315  
cvm                                                          1.0  
cvmed                                                   0.851816  
cvmode         0

In [389]:
early_morning_delay.describe()

route_id     agency_id    route_type    service_id  direction_id  \
count  29190.000000  29190.000000  29190.000000  29190.000000  29190.000000   
mean     539.941487      6.028092      2.579342   3898.425557      0.509490   
min       18.000000      1.000000      0.000000      3.000000      0.000000   
25%      602.000000      6.000000      3.000000     64.000000      0.000000   
50%      607.000000      6.000000      3.000000     64.000000      1.000000   
75%      612.000000      6.000000      3.000000    179.000000      1.000000   
max      690.000000      8.000000      3.000000  27312.000000      1.000000   
std      195.403337      0.240405      1.041661   9370.493248      0.499919   

           shape_id       stop_id            actual_arrival_time  \
count  29190.000000  29190.000000                          28330   
mean    3709.950291   2287.541727  2023-07-16 12:24:41.798270464   
min        7.000000     43.000000            2023-07-01 03:00:00   
25%     1945.000000   1203.000000  2023-07-09 05:16:48.750000128   
50%     2898.000000   1455.000000     2023-07-17 05:09:22.500000   
75%     5633.000000   1711.000000            2023-07-24 05:33:15   
max    10396.000000   9780.000000            2023-08-01 03:19:00   
std     2692.937526   2398.487536                            NaN   

               actual_departure_time  vrs_timestamp  ...  \
count                          29190   29190.000000  ...   
mean   2023-07-16 12:21:54.101747200   48529.056252  ...   
min              2023-07-01 03:00:15   10307.000000  ...   
25%    2023-07-09 05:00:56.249999872   34804.000000  ...   
50%              2023-07-17 05:09:30   40804.000000  ...   
75%              2023-07-24 05:33:45   43304.000000  ...   
max              2023-08-01 03:19:15  235807.000000  ...   
std                              NaN   44696.079439  ...   

       departure_delay_float actual_arrival_time_float  \
count           29190.000000              29190.000000   
mean                0.926944              49155.014217   
min                 0.000000                  0.000000   
25%                 0.250000              50415.000000   
50%                 0.500000              52830.000000   
75%                 0.750000              54530.000000   
max                51.500000              60000.000000   
std                 3.432776              10667.375496   

      actual_departure_time_float arrival_delay_span   weather_int  \
count                29190.000000            29190.0  29190.000000   
mean                 50594.649880                0.0      0.181877   
min                  30015.000000                0.0      0.000000   
25%                  50720.000000                0.0      0.000000   
50%                  52930.000000                0.0      0.000000   
75%                  54615.000000                0.0      0.000000   
max                  60230.000000                0.0      2.000000   
std                   6526.413045                0.0      0.443970   

       time_span_int_arrival       weekend  time_span_int  delay_category  \
count           29190.000000  29190.000000   29190.000000    29190.000000   
mean                7.761425      0.681809       7.995444        0.647345   
min                 0.000000      0.000000       1.000000       -1.000000   
25%                 8.000000      0.000000       8.000000        0.000000   
50%                 8.000000      0.000000       8.000000        1.000000   
75%                 8.000000      1.000000       8.000000        1.000000   
max                 8.000000      3.000000       8.000000        1.000000   
std                 1.359730      0.999685       0.178535        0.535932   

       cancelled_trip  
count         29190.0  
mean              0.0  
min               0.0  
25%               0.0  
50%               0.0  
75%               0.0  
max               0.0  
std               0.0  

[8 rows x 38 columns]

In [390]:
early_morning_no_delay.describe()

route_id     agency_id    route_type    service_id  direction_id  \
count  20057.000000  20057.000000  20057.000000  20057.000000  20057.000000   
mean     459.765718      6.518921      2.142793   7213.496585      0.470060   
min       16.000000      1.000000      0.000000      3.000000      0.000000   
25%       66.000000      6.000000      0.000000     64.000000      0.000000   
50%      604.000000      6.000000      3.000000     64.000000      0.000000   
75%      611.000000      6.000000      3.000000  26678.000000      1.000000   
max      884.000000     12.000000      3.000000  29145.000000      1.000000   
std      267.027471      1.701015      1.355326  11857.653541      0.499115   

           shape_id       stop_id            actual_arrival_time  \
count  20057.000000  20057.000000                          15356   
mean    4149.068405   1961.364112  2023-07-16 04:24:50.569484032   
min        6.000000     43.000000            2023-07-01 03:00:00   
25%     1975.000000   1115.000000            2023-07-08 05:36:30   
50%     3113.000000   1374.000000            2023-07-17 03:08:45   
75%     6368.000000   1607.000000            2023-07-24 05:33:45   
max    10396.000000   9780.000000            2023-08-01 03:15:45   
std     2786.707451   2147.717758                            NaN   

               actual_departure_time  vrs_timestamp  ...  \
count                          20057   20057.000000  ...   
mean   2023-07-16 04:52:10.958767616   43862.809543  ...   
min              2023-07-01 03:00:00   10304.000000  ...   
25%              2023-07-08 05:42:00   33805.000000  ...   
50%              2023-07-17 02:43:00   40307.000000  ...   
75%              2023-07-24 05:31:00   42805.000000  ...   
max              2023-08-01 03:16:00  235807.000000  ...   
std                              NaN   34912.602271  ...   

       departure_delay_float actual_arrival_time_float  \
count           20057.000000              20057.000000   
mean                0.023899              38888.152017   
min                 0.000000                  0.000000   
25%                 0.000000              30745.000000   
50%                 0.000000              51740.000000   
75%                 0.000000              54045.000000   
max                45.000000              60100.000000   
std                 0.444114              22166.880333   

      actual_departure_time_float arrival_delay_span   weather_int  \
count                20057.000000            20057.0  20057.000000   
mean                 50883.950740                0.0      0.186818   
min                  23615.000000                0.0      0.000000   
25%                  50800.000000                0.0      0.000000   
50%                  52900.000000                0.0      0.000000   
75%                  54600.000000                0.0      0.000000   
max                  60300.000000                0.0      2.000000   
std                   5978.261811                0.0      0.437509   

       time_span_int_arrival       weekend  time_span_int  delay_category  \
count           20057.000000  20057.000000   20057.000000    20057.000000   
mean                6.103754      0.589669       7.965648       -0.230294   
min                 0.000000      0.000000       0.000000       -1.000000   
25%                 8.000000      0.000000       8.000000        0.000000   
50%                 8.000000      0.000000       8.000000        0.000000   
75%                 8.000000      1.000000       8.000000        0.000000   
max                 8.000000      3.000000       8.000000        1.000000   
std                 3.401816      0.920476       0.509940        0.430633   

       cancelled_trip  
count         20057.0  
mean              0.0  
min               0.0  
25%               0.0  
50%               0.0  
75%               0.0  
max               0.0  
std               0.0  

[8 rows x 38 columns]

In [391]:
early_morning_nan_delay.describe()

route_id     agency_id    route_type    service_id  direction_id  \
count  31305.000000  31305.000000  31305.000000  31305.000000  31305.000000   
mean     546.038844      6.178182      2.617058   4743.441431      0.496023   
min       16.000000      1.000000      0.000000      3.000000      0.000000   
25%      601.000000      6.000000      3.000000     64.000000      0.000000   
50%      608.000000      6.000000      3.000000     64.000000      0.000000   
75%      612.000000      6.000000      3.000000    151.000000      1.000000   
max      884.000000     12.000000      3.000000  28777.000000      1.000000   
std      193.368008      0.966241      1.001106  10181.548392      0.499992   

           shape_id       stop_id actual_arrival_time actual_departure_time  \
count  31305.000000  31305.000000                   0                     0   
mean    3865.751765   2245.335953                 NaT                   NaT   
min        6.000000     43.000000                 NaT                   NaT   
25%     1945.000000   1201.000000                 NaT                   NaT   
50%     2936.000000   1414.000000                 NaT                   NaT   
75%     5907.000000   1681.000000                 NaT                   NaT   
max    10396.000000   9780.000000                 NaT                   NaT   
std     2747.239998   2365.013297                 NaN                   NaN   

       vrs_timestamp  ...  departure_delay_float actual_arrival_time_float  \
count   31305.000000  ...                    0.0                   31305.0   
mean    46823.691104  ...                    NaN                       0.0   
min     10305.000000  ...                    NaN                       0.0   
25%     35806.000000  ...                    NaN                       0.0   
50%     41804.000000  ...                    NaN                       0.0   
75%     43305.000000  ...                    NaN                       0.0   
max    235807.000000  ...                    NaN                       0.0   
std     35961.468919  ...                    NaN                       0.0   

      actual_departure_time_float arrival_delay_span   weather_int  \
count                     31305.0            31305.0  31305.000000   
mean                          0.0                0.0      0.199233   
min                           0.0                0.0      0.000000   
25%                           0.0                0.0      0.000000   
50%                           0.0                0.0      0.000000   
75%                           0.0                0.0      0.000000   
max                           0.0                0.0      2.000000   
std                           0.0                0.0      0.441519   

       time_span_int_arrival       weekend  time_span_int  delay_category  \
count                31305.0  31305.000000        31305.0         31305.0   
mean                     0.0      0.497908            0.0            -1.0   
min                      0.0      0.000000            0.0            -1.0   
25%                      0.0      0.000000            0.0            -1.0   
50%                      0.0      0.000000            0.0            -1.0   
75%                      0.0      1.000000            0.0            -1.0   
max                      0.0      3.000000            0.0            -1.0   
std                      0.0      0.836571            0.0             0.0   

       cancelled_trip  
count         31305.0  
mean              1.0  
min               1.0  
25%               1.0  
50%               1.0  
75%               1.0  
max               1.0  
std               0.0  

[8 rows x 38 columns]

#### Weekday vs. Weekend

We will take a look onto weekdays from Monday to Thursday, and then Friday, Saturday and Sunday each seperately. I do this because I assume that Friday is split into two usage patterns: in the morning, midday, and eveneing rushhour, there will be a similar usage to the other working days. But in the evening, there will be a difference because the weekend start. Saturday is a weekend day with activities, that will differ to Friday pre-evening, but also from Sunday since on Sunday, stores are closed and city activities differ.

In [392]:
during_week_delay = delay[delay['weekday'].isin(['Monday', 'Tuesday', 'Wednesday', 'Thursday'])]
during_week_delay


route_id  agency_id route_short_name  route_type route_type_name  \
134940        607          6              607           3             Bus   
134942        608          6              608           3             Bus   
134949        612          6              612           3             Bus   
134952        610          6              610           3             Bus   
134956        610          6              610           3             Bus   
...           ...        ...              ...         ...             ...   
2564839       689          6               N9           3             Bus   
2564841       689          6               N9           3             Bus   
2564843       688          6               N8           3             Bus   
2564847       688          6               N8           3             Bus   
2564851       688          6               N8           3             Bus   

                               agency_name  service_id  \
134940   SWB Stadtwerke Bonn Verkehrs GmbH           3   
134942   SWB Stadtwerke Bonn Verkehrs GmbH         151   
134949   SWB Stadtwerke Bonn Verkehrs GmbH         151   
134952   SWB Stadtwerke Bonn Verkehrs GmbH         151   
134956   SWB Stadtwerke Bonn Verkehrs GmbH         151   
...                                    ...         ...   
2564839  SWB Stadtwerke Bonn Verkehrs GmbH          43   
2564841  SWB Stadtwerke Bonn Verkehrs GmbH          43   
2564843  SWB Stadtwerke Bonn Verkehrs GmbH         179   
2564847  SWB Stadtwerke Bonn Verkehrs GmbH         179   
2564851  SWB Stadtwerke Bonn Verkehrs GmbH         179   

                                                   trip_id  \
134940   6070037-607-006-1357.2.21:232300-45-1_84FA3930...   
134942   6080478-608-006-1574.2.24:232400-47-1_ED5E7013...   
134949   6120436-612-006-1280.2.22:235800-16-1_5BDB204A...   
134952   6100520-610-006-1341.2.24:232100-40-1_E20EB82F...   
134956   6100522-610-006-1341.2.24:235100-40-1_271C1DF5...   
...                                                    ...   
2564839  6890005-689-006-687.2.34:263500-53-1_2AFE8F0F-...   
2564841  6890005-689-006-687.2.34:263500-53-1_2AFE8F0F-...   
2564843  6880005-688-006-687.2.32:263500-36-1_5350170A-...   
2564847  6880005-688-006-687.2.32:263500-36-1_5350170A-...   
2564851  6880005-688-006-687.2.32:263500-36-1_5350170A-...   

                         trip_headsign  direction_id  ...  delay_span  \
134940                      Ramersdorf             0  ...         0-5   
134942              Hardthöhe/Südwache             1  ...         0-5   
134949                  Koblenzer Str.             1  ...         0-5   
134952   Bad Godesberg Bf / Rheinallee             1  ...         0-5   
134956   Bad Godesberg Bf / Rheinallee             1  ...         0-5   
...                                ...           ...  ...         ...   
2564839                       Bonn Hbf             0  ...         0-5   
2564841                       Bonn Hbf             0  ...         0-5   
2564843                       Bonn Hbf             0  ...         0-5   
2564847                       Bonn Hbf             0  ...         0-5   
2564851                       Bonn Hbf             0  ...         0-5   

         arrival_delay_span weather_int time_span_arrival  \
134940                    0           0                 0   
134942                    0           0                 0   
134949                    0           0                 0   
134952                    0           0                 0   
134956                    0           0                 0   
...                     ...         ...               ...   
2564839                   0           1     early morning   
2564841                   0           1     early morning   
2564843                   0           1     early morning   
2564847                   0           1     early morning   
2564851                   0           1     early morning   

         time_span_int_arrival  

In [393]:
get_stats(during_week_delay, ['tier_trips_count', 'tier_trips_end_at_station_count', 'nextbike_trips_count', 'nextbike_trips_end_at_station_count', 'current_temp', 'current_precipitation_volume'])

/tmp/ipykernel_2575952/41814695.py:51: RuntimeWarning: invalid value encountered in scalar divide
  qd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:55: RuntimeWarning: invalid value encountered in scalar divide
  cvqd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:51: RuntimeWarning: invalid value encountered in scalar divide
  qd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:55: RuntimeWarning: invalid value encountered in scalar divide
  cvqd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:51: RuntimeWarning: invalid value encountered in scalar divide
  qd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:55: RuntimeWarning: invalid value encountered in scalar divide
  cvqd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:51: RuntimeWarning: invalid value encountered in scalar divide
  qd = iqr / (percentile_75 + percenti

column                                        tier_trips_count  \
rows                                                    585948   
sum                                                       7534   
mean                                                  0.012858   
median                                                     0.0   
mode               0    0
Name: tier_trips_count, dtype: int64   
max                                                          5   
min                                                          0   
std_dev                                               0.120861   
variance                                              0.014607   
skewness                                             10.831351   
kurtosis                                            150.531267   
percentile_25                                              0.0   
percentile_75                                              0.0   
iqr                                                        0.0   
range                                                        5   
cv                                                     9.39981   
qd                                                         NaN   
cs                                                   89.618359   
ck                                                  1245.49242   
cvs                                                  89.618359   
cvk                                                 1245.49242   
cvcs                                                 89.618359   
cvck                                                1245.49242   
cvcv                                                   9.39981   
cvqd                                                       NaN   
cvr                                                 388.869127   
cvm                                                        1.0   
cvmed                                                      0.0   
cvmode         0    0.0
Name: tier_trips_count, dtype: float64   

column                           tier_trips_end_at_station_count  \
rows                                                      585948   
sum                                                         6187   
mean                                                    0.010559   
median                                                       0.0   
mode           0    0
Name: tier_trips_end_at_station_count, ...   
max                                                            4   
min                                                            0   
std_dev                                                 0.109172   
variance                                                0.011919   
skewness                                               11.742967   
kurtosis                                              170.511338   
percentile_25                                                0.0   
percentile_75                                                0.0   
iqr                                                          0.0   
range                                                          4   
cv                                                     10.339313   
qd                                                           NaN   
cs                                                    107.563543   
ck                                                   1561.854311   
cvs                                                   107.563543   
cvk                                                  1561.854311   
cvcs                                                  107.563543   
cvck                                                 1561.854311   
cvcv                                                   10.339313   
cvqd                                                         NaN   
cvr                                                   378.825279   
cvm                                                          1.0   
cvmed                                                        0.0   
cvmode         0    0.0
Name: tier_trips_end_at

In [394]:
during_week_delay_tier = check_micromobility_datasets('tier', during_week_delay)

In [395]:
during_week_delay_tier.describe()

tier_trips_id          tier_trips_start_time  \
count   5.015000e+03                           5015   
mean    7.952702e+08  2023-07-14 20:29:09.990030080   
min     7.822646e+08            2023-07-03 07:50:00   
25%     7.823603e+08            2023-07-06 19:25:00   
50%     7.824481e+08            2023-07-12 19:25:00   
75%     8.087121e+08            2023-07-20 11:55:00   
max     8.323097e+08            2023-08-01 01:45:00   
std     1.479361e+07                            NaN   

                 tier_trips_end_time              trip_duration  \
count                           5015                       5015   
mean   2023-07-14 20:42:56.721834496  0 days 00:13:46.731804586   
min              2023-07-03 08:00:00            0 days 00:05:00   
25%              2023-07-06 19:35:00            0 days 00:10:00   
50%              2023-07-12 19:40:00            0 days 00:10:00   
75%              2023-07-20 12:07:30            0 days 00:15:00   
max              2023-08-01 02:05:00            0 days 01:45:00   
std                              NaN  0 days 00:09:13.132273495   

       trip_distance_kilometers  trip_distance_meters  start_stop_id  \
count               5015.000000           5015.000000    3545.000000   
mean                   1.669127           1669.126578    1391.154020   
min                    0.100174            100.173813      43.000000   
25%                    0.721802            721.801713    1102.000000   
50%                    1.287888           1287.888398    1128.000000   
75%                    2.188249           2188.249262    1240.000000   
max                   13.908704          13908.703513    9780.000000   
std                    1.375979           1375.979466    1373.185498   

       end_stop_id  trip_duration_seconds  
count  2800.000000            5015.000000  
mean   1382.204286             826.731805  
min      43.000000             300.000000  
25%    1102.000000             600.000000  
50%    1145.000000             600.000000  
75%    1240.000000             900.000000  
max    9780.000000            6300.000000  
std    1400.083719             553.132273

In [396]:
get_stats(during_week_delay_tier, ['trip_duration_seconds', 'trip_distance_kilometers'])

column                                     trip_duration_seconds  \
rows                                                        5015   
sum                                                    4146060.0   
mean                                                  826.731805   
median                                                     600.0   
mode           0    600.0
Name: trip_duration_seconds, dtype:...   
max                                                       6300.0   
min                                                        300.0   
std_dev                                               553.132273   
variance                                           305955.311982   
skewness                                                3.882083   
kurtosis                                               24.558281   
percentile_25                                              600.0   
percentile_75                                              900.0   
iqr                                                        300.0   
range                                                     6000.0   
cv                                                      0.669059   
qd                                                           0.2   
cs                                                      0.007018   
ck                                                      0.044399   
cvs                                                     0.007018   
cvk                                                     0.044399   
cvcs                                                    0.007018   
cvck                                                    0.044399   
cvcv                                                    0.669059   
cvqd                                                         0.2   
cvr                                                     7.257493   
cvm                                                          1.0   
cvmed                                                   0.725749   
cvmode         0    0.725749
Name: trip_duration_seconds, dty...   

column                                  trip_distance_kilometers  
rows                                                        5015  
sum                                                   8370.66979  
mean                                                    1.669127  
median                                                  1.287888  
mode           0        0.100174
1        0.100631
2        0...  
max                                                    13.908704  
min                                                     0.100174  
std_dev                                                 1.375979  
variance                                                1.893319  
skewness                                                1.980112  
kurtosis                                                 6.30678  
percentile_25                                           0.721802  
percentile_75                                           2.188249  
iqr                                                     1.466448  
range                                                   13.80853  
cv                                                      0.824371  
qd                                                      0.503925  
cs                                                      1.439056  
ck                                                      4.583484  
cvs                                                     1.439056  
cvk                                                     4.583484  
cvcs                                                    1.439056  
cvck                                                    4.583484  
cvcv                                                    0.824371  
cvqd                                                    0.503925  
cvr                                                     8.272907  
cvm                                                          1.0  
cvmed                                                   0.771594  
cvmode         0

In [397]:
# get entries where trips start and end at station
during_week_delay_tier_station_station = during_week_delay_tier[during_week_delay_tier['end_stop_id'].notna() & during_week_delay_tier['start_stop_id'].notna()]
during_week_delay_tier_station_station

tier_trips_id tier_trips_start_time tier_trips_end_time vehicle type  \
3235740      782415153   2023-07-03 07:50:00 2023-07-03 08:00:00    e-scooter   
3229350      782409323   2023-07-03 08:15:00 2023-07-03 08:30:00    e-scooter   
3104259      782327365   2023-07-03 08:15:00 2023-07-03 08:25:00    e-scooter   
3249701      782427914   2023-07-03 08:20:00 2023-07-03 08:30:00    e-scooter   
3248287      782426608   2023-07-03 08:25:00 2023-07-03 08:40:00    e-scooter   
...                ...                   ...                 ...          ...   
3422531      832205256   2023-07-31 23:25:00 2023-08-01 00:00:00    e-scooter   
3485603      832265823   2023-07-31 23:25:00 2023-08-01 00:00:00    e-scooter   
3398184      832181971   2023-08-01 00:10:00 2023-08-01 00:20:00    e-scooter   
3326567      832125594   2023-08-01 01:45:00 2023-08-01 02:05:00    e-scooter   
3464513      832245595   2023-08-01 01:45:00 2023-08-01 02:05:00    e-scooter   

          trip_duration  trip_distance_kilometers  trip_distance_meters  \
3235740 0 days 00:10:00                  0.670067            670.067486   
3229350 0 days 00:15:00                  2.303271           2303.270867   
3104259 0 days 00:10:00                  0.798354            798.354099   
3249701 0 days 00:10:00                  0.705784            705.784020   
3248287 0 days 00:15:00                  1.863846           1863.846151   
...                 ...                       ...                   ...   
3422531 0 days 00:35:00                  1.787106           1787.106290   
3485603 0 days 00:35:00                  1.774445           1774.445116   
3398184 0 days 00:10:00                  0.649892            649.892254   
3326567 0 days 00:20:00                  0.308480            308.479763   
3464513 0 days 00:20:00                  0.288030            288.030156   

         start_stop_id                            start_stop_name  \
3235740         1512.0                        Bonn Adelheidisstr.   
3229350         1500.0                 Bonn Konrad-Adenauer-Platz   
3104259         1106.0                      Bonn Thomas-Mann-Str.   
3249701         1292.0                            Bonn Kiefernweg   
3248287         1144.0                         Bonn Beethovenstr.   
...                ...                                        ...   
3422531         1153.0                              Bonn Heerstr.   
3485603         1153.0                              Bonn Heerstr.   
3398184         1255.0                Bonn Graf-Stauffenberg-Str.   
3326567         1115.0  Bonn Bertha-Von-Suttner-Pl./Beethovenhaus   
3464513         1115.0  Bonn Bertha-Von-Suttner-Pl./Beethovenhaus   

                                         start_buffer_zone  end_stop_id  \
3235740  801621     POLYGON ((7.157885983913106 50.7227...       1522.0   
3229350  801621     POLYGON ((7.157885983913106 50.7227...       1102.0   
3104259  801621     POLYGON ((7.157885983913106 50.7227...       1143.0   
3249701  801621     POLYGON ((7.157885983913106 50.7227...       1293.0   
3248287  801621     POLYGON ((7.157885983913106 50.7227...       1620.0   
...                                                    ...          ...   
3422531  801621     POLYGON ((7.157885983913106 50.7227...       1190.0   
3485603  801621     POLYGON ((7.157885983913106 50.7227...       1190.0   
3398184  801621     POLYGON ((7.157885983913106 50.7227...       6994.0   
3326567  801621     POLYGON ((7.157885983913106 50.7227...       1111.0   
3464513  801621     POLYGON ((7.157885983913106 50.7227...       1111.0   

                       end_stop_name  \
3235740                  Bonn Vilich   
3229350           Bonn Friedensplatz   
3104259     Bonn Poppelsdorfer Allee   
3249701         Bonn Uniklinikum Süd   
3248287          Bonn Max-Bruch-Str.   
...                              ...   
3422531               Bonn Zeisigweg   
3485603               Bonn Zeisigweg   
3398184  Bonn Heinrich-Lützeler-Str.   
33265

In [398]:
during_week_delay_tier_station_station.describe()

tier_trips_id          tier_trips_start_time  \
count   2.322000e+03                           2322   
mean    7.948293e+08  2023-07-14 15:48:53.591731200   
min     7.822648e+08            2023-07-03 07:50:00   
25%     7.823560e+08            2023-07-06 18:56:15   
50%     7.824426e+08            2023-07-12 17:27:30   
75%     8.087119e+08            2023-07-19 19:18:45   
max     8.323097e+08            2023-08-01 01:45:00   
std     1.478471e+07                            NaN   

                 tier_trips_end_time              trip_duration  \
count                           2322                       2322   
mean   2023-07-14 16:01:50.206718464  0 days 00:12:56.614987080   
min              2023-07-03 08:00:00            0 days 00:05:00   
25%              2023-07-06 19:10:00            0 days 00:10:00   
50%              2023-07-12 17:35:00            0 days 00:10:00   
75%              2023-07-19 19:33:45            0 days 00:15:00   
max              2023-08-01 02:05:00            0 days 01:45:00   
std                              NaN  0 days 00:08:36.442356286   

       trip_distance_kilometers  trip_distance_meters  start_stop_id  \
count               2322.000000           2322.000000    2322.000000   
mean                   1.397465           1397.465476    1393.216624   
min                    0.100174            100.173813      43.000000   
25%                    0.620560            620.560008    1103.000000   
50%                    1.105612           1105.611792    1115.000000   
75%                    1.897479           1897.479479    1229.250000   
max                    6.834481           6834.480582    9780.000000   
std                    1.083086           1083.086284    1365.200976   

       end_stop_id  trip_duration_seconds  
count  2322.000000            2322.000000  
mean   1415.825151             776.614987  
min      43.000000             300.000000  
25%    1103.000000             600.000000  
50%    1150.000000             600.000000  
75%    1240.000000             900.000000  
max    9780.000000            6300.000000  
std    1426.092702             516.442356

In [399]:
# get statistics for the tier trips that start and end at a station
get_stats(during_week_delay_tier_station_station, ['trip_duration_seconds', 'trip_distance_kilometers'])

column                                     trip_duration_seconds  \
rows                                                        2322   
sum                                                    1803300.0   
mean                                                  776.614987   
median                                                     600.0   
mode           0    600.0
Name: trip_duration_seconds, dtype:...   
max                                                       6300.0   
min                                                        300.0   
std_dev                                               516.442356   
variance                                           266712.707367   
skewness                                                4.225289   
kurtosis                                               29.845529   
percentile_25                                              600.0   
percentile_75                                              900.0   
iqr                                                        300.0   
range                                                     6000.0   
cv                                                      0.664991   
qd                                                           0.2   
cs                                                      0.008182   
ck                                                      0.057791   
cvs                                                     0.008182   
cvk                                                     0.057791   
cvcs                                                    0.008182   
cvck                                                    0.057791   
cvcv                                                    0.664991   
cvqd                                                         0.2   
cvr                                                     7.725836   
cvm                                                          1.0   
cvmed                                                   0.772584   
cvmode         0    0.772584
Name: trip_duration_seconds, dty...   

column                                  trip_distance_kilometers  
rows                                                        2322  
sum                                                  3244.914836  
mean                                                    1.397465  
median                                                  1.105612  
mode           0       0.100174
1       0.100631
2       0.10...  
max                                                     6.834481  
min                                                     0.100174  
std_dev                                                 1.083086  
variance                                                1.173076  
skewness                                                1.499037  
kurtosis                                                2.775601  
percentile_25                                            0.62056  
percentile_75                                           1.897479  
iqr                                                     1.276919  
range                                                   6.734307  
cv                                                      0.775036  
qd                                                      0.507109  
cs                                                      1.384042  
ck                                                      2.562677  
cvs                                                     1.384042  
cvk                                                     2.562677  
cvcs                                                    1.384042  
cvck                                                    2.562677  
cvcv                                                    0.775036  
cvqd                                                    0.507109  
cvr                                                     4.818943  
cvm                                                          1.0  
cvmed                                                   0.791155  
cvmode         0

In [400]:
during_week_delay_next = check_micromobility_datasets('next', during_week_delay)

In [401]:
during_week_delay_next.describe()

nextbike_trips_id      nextbike_trips_start_time  \
count       1.450400e+04                          14504   
mean        3.794029e+07  2023-07-15 11:52:49.765582080   
min         3.771654e+07            2023-07-03 04:41:00   
25%         3.782779e+07            2023-07-10 07:41:00   
50%         3.794209e+07            2023-07-13 16:21:00   
75%         3.805009e+07            2023-07-20 16:06:00   
max         3.817174e+07            2023-08-01 00:41:00   
std         1.284045e+05                            NaN   

             nextbike_trips_end_time              trip_duration  \
count                          14504                      14504   
mean   2023-07-15 12:07:18.909266432  0 days 00:14:29.143684500   
min              2023-07-03 04:51:00            0 days 00:05:00   
25%              2023-07-10 07:56:00            0 days 00:10:00   
50%              2023-07-13 16:36:00            0 days 00:10:00   
75%              2023-07-20 16:26:00            0 days 00:15:00   
max              2023-08-01 00:46:00            0 days 02:00:00   
std                              NaN  0 days 00:09:23.735861980   

       trip_distance_kilometers  trip_distance_meters  start_stop_id  \
count              14504.000000          14504.000000   10596.000000   
mean                   1.694276           1694.276003    1288.067667   
min                    0.100260            100.260461      43.000000   
25%                    0.761708            761.708394    1102.000000   
50%                    1.319195           1319.194760    1140.000000   
75%                    2.203937           2203.937312    1223.000000   
max                   13.352880          13352.880324    9780.000000   
std                    1.409579           1409.578775    1215.762196   

       end_stop_id  trip_duration_seconds  
count  8446.000000           14504.000000  
mean   1284.871182             869.143685  
min      43.000000             300.000000  
25%     694.000000             600.000000  
50%    1143.000000             600.000000  
75%    1221.000000             900.000000  
max    9780.000000            7200.000000  
std    1281.270677             563.735862

In [402]:
get_stats(during_week_delay_next, ['trip_duration_seconds', 'trip_distance_kilometers'])

column                                     trip_duration_seconds  \
rows                                                       14504   
sum                                                   12606060.0   
mean                                                  869.143685   
median                                                     600.0   
mode           0    600.0
Name: trip_duration_seconds, dtype:...   
max                                                       7200.0   
min                                                        300.0   
std_dev                                               563.735862   
variance                                           317798.122082   
skewness                                                4.011908   
kurtosis                                               27.982579   
percentile_25                                              600.0   
percentile_75                                              900.0   
iqr                                                        300.0   
range                                                     6900.0   
cv                                                      0.648611   
qd                                                           0.2   
cs                                                      0.007117   
ck                                                      0.049638   
cvs                                                     0.007117   
cvk                                                     0.049638   
cvcs                                                    0.007117   
cvck                                                    0.049638   
cvcv                                                    0.648611   
cvqd                                                         0.2   
cvr                                                     7.938848   
cvm                                                          1.0   
cvmed                                                   0.690335   
cvmode         0    0.690335
Name: trip_duration_seconds, dty...   

column                                  trip_distance_kilometers  
rows                                                       14504  
sum                                                 24573.779144  
mean                                                    1.694276  
median                                                  1.319195  
mode           0    0.870199
Name: trip_distance_kilometers, ...  
max                                                     13.35288  
min                                                      0.10026  
std_dev                                                 1.409579  
variance                                                1.986912  
skewness                                                2.311431  
kurtosis                                                8.856439  
percentile_25                                           0.761708  
percentile_75                                           2.203937  
iqr                                                     1.442229  
range                                                   13.25262  
cv                                                      0.831965  
qd                                                      0.486312  
cs                                                      1.639802  
ck                                                      6.283039  
cvs                                                     1.639802  
cvk                                                     6.283039  
cvcs                                                    1.639802  
cvck                                                    6.283039  
cvcv                                                    0.831965  
cvqd                                                    0.486312  
cvr                                                     7.821996  
cvm                                                          1.0  
cvmed                                                   0.778619  
cvmode         0

In [403]:
# get entries where trips start and end at station
during_week_delay_next_station_station = during_week_delay_next[during_week_delay_next['end_stop_id'].notna() & during_week_delay_next['start_stop_id'].notna()]
during_week_delay_next_station_station

nextbike_trips_id nextbike_trips_start_time nextbike_trips_end_time  \
1218972           37716538       2023-07-03 04:51:00     2023-07-03 05:01:00   
1658596           37790015       2023-07-03 05:06:00     2023-07-03 05:16:00   
1471548           38036106       2023-07-03 05:16:00     2023-07-03 05:31:00   
1570657           38117565       2023-07-03 05:21:00     2023-07-03 05:31:00   
1422918           37963466       2023-07-03 05:31:00     2023-07-03 05:41:00   
...                    ...                       ...                     ...   
1333820           37861619       2023-07-31 22:16:00     2023-07-31 22:26:00   
1476595           38040111       2023-07-31 22:26:00     2023-07-31 22:41:00   
1443891           38014658       2023-07-31 22:51:00     2023-07-31 23:06:00   
1441769           38012536       2023-07-31 23:21:00     2023-07-31 23:41:00   
1592910           37753445       2023-07-31 23:31:00     2023-07-31 23:56:00   

         nextbike_trips_start_at_station  nextbike_trips_end_at_station  \
1218972                            False                          False   
1658596                            False                          False   
1471548                            False                          False   
1570657                            False                          False   
1422918                            False                          False   
...                                  ...                            ...   
1333820                            False                          False   
1476595                            False                           True   
1443891                             True                          False   
1441769                            False                          False   
1592910                            False                          False   

        vehicle type   trip_duration  trip_distance_kilometers  \
1218972         bike 0 days 00:10:00                  1.534328   
1658596         bike 0 days 00:10:00                  0.929705   
1471548         bike 0 days 00:15:00                  3.080515   
1570657         bike 0 days 00:10:00                  1.417101   
1422918         bike 0 days 00:10:00                  1.676950   
...              ...             ...                       ...   
1333820         bike 0 days 00:10:00                  0.864220   
1476595         bike 0 days 00:15:00                  1.658928   
1443891         bike 0 days 00:15:00                  2.202721   
1441769         bike 0 days 00:20:00                  3.058475   
1592910         bike 0 days 00:25:00                  4.197185   

         trip_distance_meters  \
1218972           1534.328341   
1658596            929.705305   
1471548           3080.515217   
1570657           1417.100838   
1422918           1676.950449   
...                       ...   
1333820            864.220203   
1476595           1658.927837   
1443891           2202.720792   
1441769           3058.475311   
1592910           4197.185304   

                                            start_location  \
1218972  b'\x01\x01\x00\x00\x00\xac\xad\xd8_vo\x1c@\x1e...   
1658596  b'\x01\x01\x00\x00\x00\x833\xf8\xfb\xc5l\x1c@\...   
1471548  b'\x01\x01\x00\x00\x00\xf5*2: i\x1c@F\xce\xc2\...   
1570657  b'\x01\x01\x00\x00\x00`YiR\nZ\x1c@\xdb\xfa\xe9...   
1422918  b'\x01\x01\x00\x00\x00\x1a\x88e3\x87d\x1c@kH\x...   
...                                                    ...   
1333820  b'\x01\x01\x00\x00\x00h\x06\xf1\x81\x1d_\x1c@\...   
1476595  b'\x01\x01\x00\x00\x00\xb1\xa3q\xa8\xdfe\x1c@r...   
1443891  b'\x01\x01\x00\x00\x00\x06.\x8f5#c\x1c@\x9dJ\x...   
1441769  b'\x01\x01\x00\x00\x00}\xca1Y\xdc\x7f\x1c@ILP\...   
1592910  b'\x01\x01\x00\x00\x00\xa5\xa2\xb1\xf6wv\x1c@\...   

                                              end_location  start_stop_id  \
1218972  b'\x01\x01\x00\x00\x00\x9f\xe3\xa3\xc5\x19c\x1...          684.0   
1658596  b'\x01\x01\x00\x00\x00r\xa3\xc8ZCi\x1c@\xd1\xc...

In [404]:
during_week_delay_next_station_station.describe()

nextbike_trips_id      nextbike_trips_start_time  \
count       6.836000e+03                           6836   
mean        3.794098e+07  2023-07-15 07:55:16.141018112   
min         3.771654e+07            2023-07-03 04:51:00   
25%         3.782806e+07            2023-07-10 07:24:45   
50%         3.794191e+07            2023-07-13 13:28:30   
75%         3.805017e+07            2023-07-20 15:11:00   
max         3.817174e+07            2023-07-31 23:31:00   
std         1.282340e+05                            NaN   

             nextbike_trips_end_time              trip_duration  \
count                           6836                       6836   
mean   2023-07-15 08:08:34.142773760  0 days 00:13:18.001755412   
min              2023-07-03 05:01:00            0 days 00:05:00   
25%              2023-07-10 07:36:00            0 days 00:10:00   
50%              2023-07-13 13:38:30            0 days 00:10:00   
75%              2023-07-20 15:32:15            0 days 00:15:00   
max              2023-07-31 23:56:00            0 days 02:00:00   
std                              NaN  0 days 00:07:58.851757543   

       trip_distance_kilometers  trip_distance_meters  start_stop_id  \
count               6836.000000           6836.000000    6836.000000   
mean                   1.406971           1406.970607    1303.269017   
min                    0.100260            100.260461      43.000000   
25%                    0.705052            705.051529    1102.000000   
50%                    1.161036           1161.036372    1140.000000   
75%                    1.834216           1834.215884    1223.000000   
max                    9.640671           9640.671235    9780.000000   
std                    1.047094           1047.093590    1229.064857   

       end_stop_id  trip_duration_seconds  
count  6836.000000            6836.000000  
mean   1318.593329             798.001755  
min      43.000000             300.000000  
25%    1102.000000             600.000000  
50%    1145.000000             600.000000  
75%    1221.000000             900.000000  
max    9780.000000            7200.000000  
std    1330.906634             478.851758

In [405]:
# get statistics for the tier trips that start and end at a station
get_stats(during_week_delay_next_station_station, ['trip_duration_seconds', 'trip_distance_kilometers'])

column                                     trip_duration_seconds  \
rows                                                        6836   
sum                                                    5455140.0   
mean                                                  798.001755   
median                                                     600.0   
mode           0    600.0
Name: trip_duration_seconds, dtype:...   
max                                                       7200.0   
min                                                        300.0   
std_dev                                               478.851758   
variance                                           229299.005703   
skewness                                                4.407898   
kurtosis                                               37.745372   
percentile_25                                              600.0   
percentile_75                                              900.0   
iqr                                                        300.0   
range                                                     6900.0   
cv                                                      0.600064   
qd                                                           0.2   
cs                                                      0.009205   
ck                                                      0.078825   
cvs                                                     0.009205   
cvk                                                     0.078825   
cvcs                                                    0.009205   
cvck                                                    0.078825   
cvcv                                                    0.600064   
cvqd                                                         0.2   
cvr                                                     8.646598   
cvm                                                          1.0   
cvmed                                                   0.751878   
cvmode         0    0.751878
Name: trip_duration_seconds, dty...   

column                                  trip_distance_kilometers  
rows                                                        6836  
sum                                                  9618.051069  
mean                                                    1.406971  
median                                                  1.161036  
mode           0    0.834842
Name: trip_distance_kilometers, ...  
max                                                     9.640671  
min                                                      0.10026  
std_dev                                                 1.047094  
variance                                                1.096405  
skewness                                                1.887235  
kurtosis                                                5.589597  
percentile_25                                           0.705052  
percentile_75                                           1.834216  
iqr                                                     1.129164  
range                                                   9.540411  
cv                                                      0.744219  
qd                                                      0.444681  
cs                                                      1.802355  
ck                                                      5.338202  
cvs                                                     1.802355  
cvk                                                     5.338202  
cvcs                                                    1.802355  
cvck                                                    5.338202  
cvcv                                                    0.744219  
cvqd                                                    0.444681  
cvr                                                     6.780817  
cvm                                                          1.0  
cvmed                                                   0.825203  
cvmode         0

In [406]:
during_week_no_delay = no_delay[no_delay['weekday'].isin(['Monday', 'Tuesday', 'Wednesday', 'Thursday'])]
during_week_no_delay

route_id  agency_id route_short_name  route_type route_type_name  \
134939        537          8              537           3             Bus   
134941        845         12              845           3             Bus   
134953        612          6              612           3             Bus   
134954        605          6              605           3             Bus   
134957         65          6               65           0            Tram   
...           ...        ...              ...         ...             ...   
2564809       688          6               N8           3             Bus   
2564811       687          6               N7           3             Bus   
2564817       684          6               N4           3             Bus   
2564834       689          6               N9           3             Bus   
2564845       688          6               N8           3             Bus   

                                         agency_name  service_id  \
134939      RSVG Rhein-Sieg-Verkehrsgesellschaft mbH         151   
134941   RVK Regionalverkehr Köln GmbH NL Meckenheim         151   
134953             SWB Stadtwerke Bonn Verkehrs GmbH         151   
134954             SWB Stadtwerke Bonn Verkehrs GmbH           3   
134957             SWB Stadtwerke Bonn Verkehrs GmbH       26802   
...                                              ...         ...   
2564809            SWB Stadtwerke Bonn Verkehrs GmbH         179   
2564811            SWB Stadtwerke Bonn Verkehrs GmbH         179   
2564817            SWB Stadtwerke Bonn Verkehrs GmbH         179   
2564834            SWB Stadtwerke Bonn Verkehrs GmbH          43   
2564845            SWB Stadtwerke Bonn Verkehrs GmbH         179   

                                                   trip_id  \
134939   171-537-008-687.2.36:233900-37-1_D8BD7913-E5E6...   
134941   2033-845-012-687.2.28:234800-29-1_0573B36C-FCE...   
134953   6120436-612-006-1280.2.22:235800-16-1_5BDB204A...   
134954   6050042-605-006-1415.2.22:231400-43-1_29288044...   
134957   650952-65-006-1406.1.12:235600-24-178_5A39EB23...   
...                                                    ...   
2564809  6880005-688-006-687.2.32:263500-36-1_5350170A-...   
2564811  6870005-687-006-687.2.24:263500-34-1_F0CE2D00-...   
2564817  6840005-684-006-687.2.32:263500-36-1_7F56FE12-...   
2564834  6890005-689-006-687.2.34:263500-53-1_2AFE8F0F-...   
2564845  6880005-688-006-687.2.32:263500-36-1_5350170A-...   

                         trip_headsign  direction_id  ...  delay_span  \
134939                 Oberpleis Busbf             1  ...           0   
134941                         Fronhof             0  ...           0   
134953                  Koblenzer Str.             1  ...           0   
134954                     Duisdorf Bf             1  ...           0   
134957     Oberkassel Süd/Römlinghoven             1  ...           0   
...                                ...           ...  ...         ...   
2564809                       Bonn Hbf             0  ...           0   
2564811  Bad Godesberg Bf / Rheinallee             0  ...           0   
2564817                    Am Waldrand             0  ...           0   
2564834                       Bonn Hbf             0  ...           0   
2564845                       Bonn Hbf             0  ...           0   

         arrival_delay_span weather_int time_span_arrival  \
134939                    0           0                 0   
134941                    0           0                 0   
134953                    0           0                 0   
134954                    0           0                 0   
134957                    0           0                 0   
...                     ...         ...               ...   
2564809                   0           1     early morning   
2564811                   0           1     early morning   
2564817                   0           1     early morning   
2564834                   0        

In [407]:
get_stats(during_week_no_delay, ['tier_trips_count', 'tier_trips_end_at_station_count', 'nextbike_trips_count', 'nextbike_trips_end_at_station_count', 'current_temp', 'current_precipitation_volume'])

/tmp/ipykernel_2575952/41814695.py:51: RuntimeWarning: invalid value encountered in scalar divide
  qd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:55: RuntimeWarning: invalid value encountered in scalar divide
  cvqd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:51: RuntimeWarning: invalid value encountered in scalar divide
  qd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:55: RuntimeWarning: invalid value encountered in scalar divide
  cvqd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:51: RuntimeWarning: invalid value encountered in scalar divide
  qd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:55: RuntimeWarning: invalid value encountered in scalar divide
  cvqd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:51: RuntimeWarning: invalid value encountered in scalar divide
  qd = iqr / (percentile_75 + percenti

column                                        tier_trips_count  \
rows                                                    366722   
sum                                                      10442   
mean                                                  0.028474   
median                                                     0.0   
mode               0    0
Name: tier_trips_count, dtype: int64   
max                                                          5   
min                                                          0   
std_dev                                               0.189526   
variance                                               0.03592   
skewness                                              8.338018   
kurtosis                                             95.341144   
percentile_25                                              0.0   
percentile_75                                              0.0   
iqr                                                        0.0   
range                                                        5   
cv                                                    6.656139   
qd                                                         NaN   
cs                                                   43.994029   
ck                                                   503.05011   
cvs                                                  43.994029   
cvk                                                  503.05011   
cvcs                                                 43.994029   
cvck                                                 503.05011   
cvcv                                                  6.656139   
cvqd                                                       NaN   
cvr                                                 175.599502   
cvm                                                        1.0   
cvmed                                                      0.0   
cvmode         0    0.0
Name: tier_trips_count, dtype: float64   

column                           tier_trips_end_at_station_count  \
rows                                                      366722   
sum                                                         8481   
mean                                                    0.023127   
median                                                       0.0   
mode           0    0
Name: tier_trips_end_at_station_count, ...   
max                                                            4   
min                                                            0   
std_dev                                                 0.168491   
variance                                                0.028389   
skewness                                                8.740646   
kurtosis                                               97.284831   
percentile_25                                                0.0   
percentile_75                                                0.0   
iqr                                                          0.0   
range                                                          4   
cv                                                      7.285601   
qd                                                           NaN   
cs                                                     51.876185   
ck                                                    577.390497   
cvs                                                    51.876185   
cvk                                                   577.390497   
cvcs                                                   51.876185   
cvck                                                  577.390497   
cvcv                                                    7.285601   
cvqd                                                         NaN   
cvr                                                   172.961679   
cvm                                                          1.0   
cvmed                                                        0.0   
cvmode         0    0.0
Name: tier_trips_end_at

In [408]:
during_week_no_delay_tier = check_micromobility_datasets('tier', during_week_no_delay)

In [409]:
during_week_no_delay_tier.describe()

tier_trips_id          tier_trips_start_time  \
count   4.062000e+03                           4062   
mean    7.957233e+08  2023-07-15 03:52:01.152141824   
min     7.822646e+08            2023-07-03 07:40:00   
25%     7.823612e+08            2023-07-06 22:21:15   
50%     7.824543e+08            2023-07-13 05:35:00   
75%     8.087213e+08            2023-07-20 16:22:30   
max     8.323114e+08            2023-08-01 00:10:00   
std     1.487230e+07                            NaN   

                 tier_trips_end_time              trip_duration  \
count                           4062                       4062   
mean   2023-07-15 04:05:44.992614144  0 days 00:13:43.840472673   
min              2023-07-03 07:50:00            0 days 00:05:00   
25%              2023-07-06 22:37:30            0 days 00:10:00   
50%              2023-07-13 05:47:30            0 days 00:10:00   
75%              2023-07-20 16:33:45            0 days 00:15:00   
max              2023-08-01 00:20:00            0 days 02:00:00   
std                              NaN  0 days 00:09:25.399813131   

       trip_distance_kilometers  trip_distance_meters  start_stop_id  \
count               4062.000000           4062.000000    3139.000000   
mean                   1.669261           1669.261295    1183.115005   
min                    0.100174            100.173813      43.000000   
25%                    0.716599            716.599367     687.000000   
50%                    1.305952           1305.951600    1115.000000   
75%                    2.166798           2166.797860    1292.000000   
max                   12.402037          12402.036677    9703.000000   
std                    1.383663           1383.663489    1102.920823   

       end_stop_id  trip_duration_seconds  
count  2023.000000            4062.000000  
mean   1401.900643             823.840473  
min      43.000000             300.000000  
25%    1103.000000             600.000000  
50%    1145.000000             600.000000  
75%    1240.000000             900.000000  
max    9780.000000            7200.000000  
std    1423.049713             565.399813

In [410]:
get_stats(during_week_no_delay_tier, ['trip_duration_seconds', 'trip_distance_kilometers'])

column                                     trip_duration_seconds  \
rows                                                        4062   
sum                                                    3346440.0   
mean                                                  823.840473   
median                                                     600.0   
mode           0    600.0
Name: trip_duration_seconds, dtype:...   
max                                                       7200.0   
min                                                        300.0   
std_dev                                               565.399813   
variance                                           319676.948689   
skewness                                                4.104686   
kurtosis                                               27.136368   
percentile_25                                              600.0   
percentile_75                                              900.0   
iqr                                                        300.0   
range                                                     6900.0   
cv                                                      0.686298   
qd                                                           0.2   
cs                                                       0.00726   
ck                                                      0.047995   
cvs                                                      0.00726   
cvk                                                     0.047995   
cvcs                                                     0.00726   
cvck                                                    0.047995   
cvcv                                                    0.686298   
cvqd                                                         0.2   
cvr                                                     8.375408   
cvm                                                          1.0   
cvmed                                                   0.728296   
cvmode         0    0.728296
Name: trip_duration_seconds, dty...   

column                                  trip_distance_kilometers  
rows                                                        4062  
sum                                                  6780.539382  
mean                                                    1.669261  
median                                                  1.305952  
mode           0        0.100174
1        0.100253
2        0...  
max                                                    12.402037  
min                                                     0.100174  
std_dev                                                 1.383663  
variance                                                1.914525  
skewness                                                1.948855  
kurtosis                                                5.648101  
percentile_25                                           0.716599  
percentile_75                                           2.166798  
iqr                                                     1.450198  
range                                                  12.301863  
cv                                                      0.828908  
qd                                                      0.502948  
cs                                                      1.408475  
ck                                                       4.08199  
cvs                                                     1.408475  
cvk                                                      4.08199  
cvcs                                                    1.408475  
cvck                                                     4.08199  
cvcv                                                    0.828908  
cvqd                                                    0.502948  
cvr                                                     7.369645  
cvm                                                          1.0  
cvmed                                                   0.782353  
cvmode         0

In [411]:
# get entries where trips start and end at station
during_week_no_delay_tier_station_station = during_week_no_delay_tier[during_week_no_delay_tier['end_stop_id'].notna() & during_week_no_delay_tier['start_stop_id'].notna()]
during_week_no_delay_tier_station_station

tier_trips_id tier_trips_start_time tier_trips_end_time vehicle type  \
3178291      782362104   2023-07-03 08:00:00 2023-07-03 08:15:00    e-scooter   
3229350      782409323   2023-07-03 08:15:00 2023-07-03 08:30:00    e-scooter   
3104259      782327365   2023-07-03 08:15:00 2023-07-03 08:25:00    e-scooter   
3191599      782374133   2023-07-03 08:20:00 2023-07-03 08:35:00    e-scooter   
3072484      782316708   2023-07-03 09:00:00 2023-07-03 09:15:00    e-scooter   
...                ...                   ...                 ...          ...   
3485596      832265817   2023-07-31 22:25:00 2023-07-31 22:45:00    e-scooter   
3518645      832297525   2023-07-31 22:55:00 2023-07-31 23:00:00    e-scooter   
3318827      832120317   2023-07-31 23:10:00 2023-08-01 00:20:00    e-scooter   
3421744      832204504   2023-07-31 23:15:00 2023-07-31 23:25:00    e-scooter   
3398184      832181971   2023-08-01 00:10:00 2023-08-01 00:20:00    e-scooter   

          trip_duration  trip_distance_kilometers  trip_distance_meters  \
3178291 0 days 00:15:00                  4.184828           4184.827793   
3229350 0 days 00:15:00                  2.303271           2303.270867   
3104259 0 days 00:10:00                  0.798354            798.354099   
3191599 0 days 00:15:00                  1.523797           1523.796888   
3072484 0 days 00:15:00                  2.516812           2516.811843   
...                 ...                       ...                   ...   
3485596 0 days 00:20:00                  1.171579           1171.578745   
3518645 0 days 00:05:00                  0.704362            704.361980   
3318827 0 days 01:10:00                  0.117849            117.848655   
3421744 0 days 00:10:00                  1.002491           1002.491082   
3398184 0 days 00:10:00                  0.649892            649.892254   

         start_stop_id                            start_stop_name  \
3178291          697.0                             Bonn Dransdorf   
3229350         1500.0                 Bonn Konrad-Adenauer-Platz   
3104259         1106.0                      Bonn Thomas-Mann-Str.   
3191599         1175.0                            Bonn Lvr-Klinik   
3072484         1504.0                              Bonn Beuel Bf   
...                ...                                        ...   
3485596          686.0                     Bonn Universität/Markt   
3518645         1115.0  Bonn Bertha-Von-Suttner-Pl./Beethovenhaus   
3318827         1115.0  Bonn Bertha-Von-Suttner-Pl./Beethovenhaus   
3421744         1504.0                              Bonn Beuel Bf   
3398184         1255.0                Bonn Graf-Stauffenberg-Str.   

                                         start_buffer_zone  end_stop_id  \
3178291  801621     POLYGON ((7.157885983913106 50.7227...       1194.0   
3229350  801621     POLYGON ((7.157885983913106 50.7227...       1102.0   
3104259  801621     POLYGON ((7.157885983913106 50.7227...       1143.0   
3191599  801621     POLYGON ((7.157885983913106 50.7227...        688.0   
3072484  801621     POLYGON ((7.157885983913106 50.7227...        685.0   
...                                                    ...          ...   
3485596  801621     POLYGON ((7.157885983913106 50.7227...       1153.0   
3518645  801621     POLYGON ((7.157885983913106 50.7227...       1161.0   
3318827  801621     POLYGON ((7.157885983913106 50.7227...       1115.0   
3421744  801621     POLYGON ((7.157885983913106 50.7227...       1126.0   
3398184  801621     POLYGON ((7.157885983913106 50.7227...       6994.0   

                                     end_stop_name  \
3178291                  Bonn Eifelstr./Macke-Haus   
3229350                         Bonn Friedensplatz   
3104259                   Bonn Poppelsdorfer Allee   
3191599                                  Bonn West   
3072484                             Bonn Juridicum   
...                                            ...   
3485596                    

In [412]:
during_week_no_delay_tier_station_station.describe()

tier_trips_id          tier_trips_start_time  \
count   1.801000e+03                           1801   
mean    7.951321e+08  2023-07-14 21:22:31.948917248   
min     7.822648e+08            2023-07-03 08:00:00   
25%     7.823524e+08            2023-07-06 18:45:00   
50%     7.824465e+08            2023-07-12 18:25:00   
75%     8.087165e+08            2023-07-20 12:15:00   
max     8.323019e+08            2023-08-01 00:10:00   
std     1.475748e+07                            NaN   

                 tier_trips_end_time              trip_duration  \
count                           1801                       1801   
mean   2023-07-14 21:35:20.322043392  0 days 00:12:48.373126041   
min              2023-07-03 08:15:00            0 days 00:05:00   
25%              2023-07-06 19:00:00            0 days 00:10:00   
50%              2023-07-12 18:40:00            0 days 00:10:00   
75%              2023-07-20 12:30:00            0 days 00:15:00   
max              2023-08-01 00:20:00            0 days 01:45:00   
std                              NaN  0 days 00:08:36.804354373   

       trip_distance_kilometers  trip_distance_meters  start_stop_id  \
count               1801.000000           1801.000000    1801.000000   
mean                   1.410683           1410.683415    1216.163798   
min                    0.100174            100.173813      43.000000   
25%                    0.614355            614.355144     687.000000   
50%                    1.101520           1101.519641    1115.000000   
75%                    1.918816           1918.816171    1221.000000   
max                    8.674586           8674.585792    9703.000000   
std                    1.121143           1121.142740    1090.405792   

       end_stop_id  trip_duration_seconds  
count  1801.000000            1801.000000  
mean   1425.422543             768.373126  
min      43.000000             300.000000  
25%    1106.000000             600.000000  
50%    1150.000000             600.000000  
75%    1240.000000             900.000000  
max    9780.000000            6300.000000  
std    1447.535330             516.804354

In [413]:
# get statistics for the tier trips that start and end at a station
get_stats(during_week_no_delay_tier_station_station, ['trip_duration_seconds', 'trip_distance_kilometers'])

column                                     trip_duration_seconds  \
rows                                                        1801   
sum                                                    1383840.0   
mean                                                  768.373126   
median                                                     600.0   
mode           0    600.0
Name: trip_duration_seconds, dtype:...   
max                                                       6300.0   
min                                                        300.0   
std_dev                                               516.804354   
variance                                             267086.7407   
skewness                                                4.600856   
kurtosis                                               35.080488   
percentile_25                                              600.0   
percentile_75                                              900.0   
iqr                                                        300.0   
range                                                     6000.0   
cv                                                      0.672596   
qd                                                           0.2   
cs                                                      0.008903   
ck                                                       0.06788   
cvs                                                     0.008903   
cvk                                                      0.06788   
cvcs                                                    0.008903   
cvck                                                     0.06788   
cvcv                                                    0.672596   
cvqd                                                         0.2   
cvr                                                     7.808706   
cvm                                                          1.0   
cvmed                                                   0.780871   
cvmode         0    0.780871
Name: trip_duration_seconds, dty...   

column                                  trip_distance_kilometers  
rows                                                        1801  
sum                                                   2540.64083  
mean                                                    1.410683  
median                                                   1.10152  
mode           0       0.100174
1       0.100253
2       0.10...  
max                                                     8.674586  
min                                                     0.100174  
std_dev                                                 1.121143  
variance                                                1.256961  
skewness                                                1.622502  
kurtosis                                                3.671508  
percentile_25                                           0.614355  
percentile_75                                           1.918816  
iqr                                                     1.304461  
range                                                   8.574412  
cv                                                      0.794751  
qd                                                      0.514952  
cs                                                      1.447186  
ck                                                      3.274791  
cvs                                                     1.447186  
cvk                                                     3.274791  
cvcs                                                    1.447186  
cvck                                                    3.274791  
cvcv                                                    0.794751  
cvqd                                                    0.514952  
cvr                                                     6.078197  
cvm                                                          1.0  
cvmed                                                   0.780841  
cvmode         0

In [414]:
during_week_no_delay_next = check_micromobility_datasets('next', during_week_no_delay)

In [415]:
during_week_no_delay_next.describe()

nextbike_trips_id      nextbike_trips_start_time  \
count       1.117800e+04                          11178   
mean        3.793915e+07  2023-07-15 17:28:36.849168128   
min         3.771654e+07            2023-07-03 00:06:00   
25%         3.782615e+07            2023-07-10 08:36:00   
50%         3.794079e+07            2023-07-13 19:06:00   
75%         3.804994e+07            2023-07-20 18:34:45   
max         3.817174e+07            2023-08-01 00:46:00   
std         1.289827e+05                            NaN   

             nextbike_trips_end_time              trip_duration  \
count                          11178                      11178   
mean   2023-07-15 17:42:55.024154624  0 days 00:14:18.174986580   
min              2023-07-03 00:26:00            0 days 00:05:00   
25%              2023-07-10 08:52:15            0 days 00:10:00   
50%              2023-07-13 19:18:30            0 days 00:10:00   
75%              2023-07-20 18:54:45            0 days 00:15:00   
max              2023-08-01 01:06:00            0 days 02:00:00   
std                              NaN  0 days 00:09:19.051745254   

       trip_distance_kilometers  trip_distance_meters  start_stop_id  \
count              11178.000000          11178.000000    9309.000000   
mean                   1.662378           1662.378430    1106.032657   
min                    0.100260            100.260461      43.000000   
25%                    0.785301            785.301371     687.000000   
50%                    1.295302           1295.301831    1115.000000   
75%                    2.099186           2099.186454    1221.000000   
max                   13.602096          13602.096364    9780.000000   
std                    1.382955           1382.954757     911.652138   

       end_stop_id  trip_duration_seconds  
count  6324.000000           11178.000000  
mean   1236.926154             858.174987  
min      43.000000             300.000000  
25%    1102.000000             600.000000  
50%    1144.000000             600.000000  
75%    1221.000000             900.000000  
max    9780.000000            7200.000000  
std    1107.311599             559.051745

In [416]:
get_stats(during_week_no_delay_next, ['trip_duration_seconds', 'trip_distance_kilometers'])

column                                     trip_duration_seconds  \
rows                                                       11178   
sum                                                    9592680.0   
mean                                                  858.174987   
median                                                     600.0   
mode           0    600.0
Name: trip_duration_seconds, dtype:...   
max                                                       7200.0   
min                                                        300.0   
std_dev                                               559.051745   
variance                                           312538.853872   
skewness                                                4.072162   
kurtosis                                               28.478831   
percentile_25                                              600.0   
percentile_75                                              900.0   
iqr                                                        300.0   
range                                                     6900.0   
cv                                                      0.651443   
qd                                                           0.2   
cs                                                      0.007284   
ck                                                      0.050941   
cvs                                                     0.007284   
cvk                                                     0.050941   
cvcs                                                    0.007284   
cvck                                                    0.050941   
cvcv                                                    0.651443   
cvqd                                                         0.2   
cvr                                                     8.040318   
cvm                                                          1.0   
cvmed                                                   0.699158   
cvmode         0    0.699158
Name: trip_duration_seconds, dty...   

column                                  trip_distance_kilometers  
rows                                                       11178  
sum                                                 18582.066088  
mean                                                    1.662378  
median                                                  1.295302  
mode           0    0.222838
1    0.982570
Name: trip_distanc...  
max                                                    13.602096  
min                                                      0.10026  
std_dev                                                 1.382955  
variance                                                1.912564  
skewness                                                2.379652  
kurtosis                                                9.212357  
percentile_25                                           0.785301  
percentile_75                                           2.099186  
iqr                                                     1.313885  
range                                                  13.501836  
cv                                                      0.831913  
qd                                                        0.4555  
cs                                                      1.720701  
ck                                                      6.661358  
cvs                                                     1.720701  
cvk                                                     6.661358  
cvcs                                                    1.720701  
cvck                                                    6.661358  
cvcv                                                    0.831913  
cvqd                                                      0.4555  
cvr                                                     8.121999  
cvm                                                          1.0  
cvmed                                                   0.779186  
cvmode         0

In [417]:
# get entries where trips start and end at station
during_week_no_delay_next_station_station = during_week_no_delay_next[during_week_no_delay_next['end_stop_id'].notna() & during_week_no_delay_next['start_stop_id'].notna()]
during_week_no_delay_next_station_station

nextbike_trips_id nextbike_trips_start_time nextbike_trips_end_time  \
1376706           37941904       2023-07-03 00:06:00     2023-07-03 00:26:00   
1338605           37862861       2023-07-03 04:56:00     2023-07-03 05:11:00   
1665142           37796561       2023-07-03 05:16:00     2023-07-03 05:26:00   
1471548           38036106       2023-07-03 05:16:00     2023-07-03 05:31:00   
1486241           38047669       2023-07-03 05:31:00     2023-07-03 05:46:00   
...                    ...                       ...                     ...   
1539405           38089363       2023-07-31 23:31:00     2023-07-31 23:41:00   
1466477           38032070       2023-07-31 23:36:00     2023-07-31 23:56:00   
1360121           37933007       2023-07-31 23:51:00     2023-07-31 23:56:00   
1360122           37933008       2023-07-31 23:56:00     2023-08-01 00:01:00   
1266955           37827223       2023-08-01 00:36:00     2023-08-01 00:41:00   

         nextbike_trips_start_at_station  nextbike_trips_end_at_station  \
1376706                            False                          False   
1338605                            False                           True   
1665142                            False                          False   
1471548                            False                          False   
1486241                            False                          False   
...                                  ...                            ...   
1539405                            False                          False   
1466477                            False                          False   
1360121                            False                           True   
1360122                             True                          False   
1266955                            False                          False   

        vehicle type   trip_duration  trip_distance_kilometers  \
1376706         bike 0 days 00:20:00                  1.911087   
1338605         bike 0 days 00:15:00                  2.516433   
1665142         bike 0 days 00:10:00                  0.743004   
1471548         bike 0 days 00:15:00                  3.080515   
1486241         bike 0 days 00:15:00                  2.152018   
...              ...             ...                       ...   
1539405         bike 0 days 00:10:00                  1.037686   
1466477         bike 0 days 00:20:00                  2.853534   
1360121         bike 0 days 00:05:00                  0.126078   
1360122         bike 0 days 00:05:00                  0.115054   
1266955         bike 0 days 00:05:00                  0.322992   

         trip_distance_meters  \
1376706           1911.087275   
1338605           2516.433094   
1665142            743.004477   
1471548           3080.515217   
1486241           2152.018454   
...                       ...   
1539405           1037.686290   
1466477           2853.534454   
1360121            126.077777   
1360122            115.054399   
1266955            322.991865   

                                            start_location  \
1376706  b'\x01\x01\x00\x00\x00\xf4\x18\xe5\x99\x97c\x1...   
1338605  b'\x01\x01\x00\x00\x00X\xfe|[\xb0d\x1c@\xef\x0...   
1665142  b'\x01\x01\x00\x00\x00\x00<\xa2Buc\x1c@\x99\r2...   
1471548  b'\x01\x01\x00\x00\x00\xf5*2: i\x1c@F\xce\xc2\...   
1486241  b'\x01\x01\x00\x00\x00\x91}\x90e\xc1d\x1c@D\xd...   
...                                                    ...   
1539405  b'\x01\x01\x00\x00\x00\xf6z\xf7\xc7{e\x1c@\xfe...   
1466477  b'\x01\x01\x00\x00\x00\xb2\xb8\xff\xc8th\x1c@\...   
1360121  b'\x01\x01\x00\x00\x00\xa7\xe7\xddXPh\x1c@`\x1...   
1360122  b'\x01\x01\x00\x00\x00\xa6}s\x7f\xf5h\x1c@\x92...   
1266955  b'\x01\x01\x00\x00\x00\xcd;N\xd1\x91\\\x1c@\xb...   

                                              end_location  start_stop_id  \
1376706  b'\x01\x01\x00\x00\x00W_]\x15\xa8e\x1c@U\xf6]\...          687.0   
1338605  b'\x01\x01\x00\x00\x007m\xc6i\x88z\x1c@\xb0\xf...

In [418]:
during_week_no_delay_next_station_station.describe()

nextbike_trips_id      nextbike_trips_start_time  \
count       5.615000e+03                           5615   
mean        3.794074e+07  2023-07-15 12:55:34.674977792   
min         3.771654e+07            2023-07-03 00:06:00   
25%         3.782889e+07            2023-07-10 06:36:00   
50%         3.794079e+07            2023-07-13 15:36:00   
75%         3.804994e+07            2023-07-20 17:41:00   
max         3.817169e+07            2023-08-01 00:36:00   
std         1.284544e+05                            NaN   

             nextbike_trips_end_time              trip_duration  \
count                           5615                       5615   
mean   2023-07-15 13:08:46.910062336  0 days 00:13:12.235084594   
min              2023-07-03 00:26:00            0 days 00:05:00   
25%              2023-07-10 06:51:00            0 days 00:10:00   
50%              2023-07-13 15:51:00            0 days 00:10:00   
75%              2023-07-20 17:56:00            0 days 00:15:00   
max              2023-08-01 00:41:00            0 days 02:00:00   
std                              NaN  0 days 00:08:24.575828746   

       trip_distance_kilometers  trip_distance_meters  start_stop_id  \
count               5615.000000           5615.000000    5615.000000   
mean                   1.389464           1389.463999    1142.844702   
min                    0.100260            100.260461      43.000000   
25%                    0.729611            729.611081     687.000000   
50%                    1.159220           1159.219550    1115.000000   
75%                    1.731232           1731.232233    1221.000000   
max                    9.640671           9640.671235    9780.000000   
std                    1.042847           1042.846598     945.401253   

       end_stop_id  trip_duration_seconds  
count  5615.000000            5615.000000  
mean   1258.849866             792.235085  
min      43.000000             300.000000  
25%    1102.000000             600.000000  
50%    1146.000000             600.000000  
75%    1221.000000             900.000000  
max    9780.000000            7200.000000  
std    1126.637556             504.575829

In [419]:
# get statistics for the tier trips that start and end at a station
get_stats(during_week_no_delay_next_station_station, ['trip_duration_seconds', 'trip_distance_kilometers'])

column                                     trip_duration_seconds  \
rows                                                        5615   
sum                                                    4448400.0   
mean                                                  792.235085   
median                                                     600.0   
mode           0    600.0
Name: trip_duration_seconds, dtype:...   
max                                                       7200.0   
min                                                        300.0   
std_dev                                               504.575829   
variance                                           254596.766956   
skewness                                                4.736893   
kurtosis                                               39.439082   
percentile_25                                              600.0   
percentile_75                                              900.0   
iqr                                                        300.0   
range                                                     6900.0   
cv                                                      0.636902   
qd                                                           0.2   
cs                                                      0.009388   
ck                                                      0.078163   
cvs                                                     0.009388   
cvk                                                     0.078163   
cvcs                                                    0.009388   
cvck                                                    0.078163   
cvcv                                                    0.636902   
cvqd                                                         0.2   
cvr                                                     8.709536   
cvm                                                          1.0   
cvmed                                                   0.757351   
cvmode         0    0.757351
Name: trip_duration_seconds, dty...   

column                                  trip_distance_kilometers  
rows                                                        5615  
sum                                                  7801.840352  
mean                                                    1.389464  
median                                                   1.15922  
mode           0    0.222838
1    0.982570
Name: trip_distanc...  
max                                                     9.640671  
min                                                      0.10026  
std_dev                                                 1.042847  
variance                                                1.087529  
skewness                                                2.069768  
kurtosis                                                6.712824  
percentile_25                                           0.729611  
percentile_75                                           1.731232  
iqr                                                     1.001621  
range                                                   9.540411  
cv                                                      0.750539  
qd                                                      0.407024  
cs                                                      1.984729  
ck                                                       6.43702  
cvs                                                     1.984729  
cvk                                                      6.43702  
cvcs                                                    1.984729  
cvck                                                     6.43702  
cvcv                                                    0.750539  
cvqd                                                    0.407024  
cvr                                                     6.866253  
cvm                                                          1.0  
cvmed                                                   0.834293  
cvmode         0

In [420]:
during_week_nan_delay = nan_delay[nan_delay['weekday'].isin(['Monday', 'Tuesday', 'Wednesday', 'Thursday'])]
during_week_nan_delay

route_id  agency_id route_short_name  route_type route_type_name  \
134943        608          6              608           3             Bus   
134944        602          6              602           3             Bus   
134945        612          6              612           3             Bus   
134946        607          6              607           3             Bus   
134948        605          6              605           3             Bus   
...           ...        ...              ...         ...             ...   
2564854       689          6               N9           3             Bus   
2564856       689          6               N9           3             Bus   
2564857       689          6               N9           3             Bus   
2564858       689          6               N9           3             Bus   
2564860       689          6               N9           3             Bus   

                               agency_name  service_id  \
134943   SWB Stadtwerke Bonn Verkehrs GmbH         151   
134944   SWB Stadtwerke Bonn Verkehrs GmbH         151   
134945   SWB Stadtwerke Bonn Verkehrs GmbH         151   
134946   SWB Stadtwerke Bonn Verkehrs GmbH           3   
134948   SWB Stadtwerke Bonn Verkehrs GmbH           3   
...                                    ...         ...   
2564854  SWB Stadtwerke Bonn Verkehrs GmbH          43   
2564856  SWB Stadtwerke Bonn Verkehrs GmbH          43   
2564857  SWB Stadtwerke Bonn Verkehrs GmbH          43   
2564858  SWB Stadtwerke Bonn Verkehrs GmbH          43   
2564860  SWB Stadtwerke Bonn Verkehrs GmbH          43   

                                                   trip_id  \
134943   6080481-608-006-1374.2.21:230900-46-1_74ED689D...   
134944   6020509-602-006-1307.2.22:232800-37-1_0CCC814E...   
134945   6120459-612-006-1763.2.21:233900-39-1_73136E71...   
134946   6070038-607-006-1584.2.22:232600-46-1_1353DC04...   
134948   6050043-605-006-1341.2.24:235100-40-1_F75C367E...   
...                                                    ...   
2564854  6890005-689-006-687.2.34:263500-53-1_2AFE8F0F-...   
2564856  6890005-689-006-687.2.34:263500-53-1_2AFE8F0F-...   
2564857  6890005-689-006-687.2.34:263500-53-1_2AFE8F0F-...   
2564858  6890005-689-006-687.2.34:263500-53-1_2AFE8F0F-...   
2564860  6890005-689-006-687.2.34:263500-53-1_2AFE8F0F-...   

              trip_headsign  direction_id  ...  delay_span  \
134943              Gielgen             0  ...           0   
134944   Agnetendorfer Str.             0  ...           0   
134945   Loki-Schmidt-Platz             0  ...           0   
134946   Hardtberg Klinikum             1  ...           0   
134948      Mondorfer Fähre             0  ...           0   
...                     ...           ...  ...         ...   
2564854            Bonn Hbf             0  ...           0   
2564856            Bonn Hbf             0  ...           0   
2564857            Bonn Hbf             0  ...           0   
2564858            Bonn Hbf             0  ...           0   
2564860            Bonn Hbf             0  ...           0   

         arrival_delay_span weather_int time_span_arrival  \
134943                    0           0                 0   
134944                    0           0                 0   
134945                    0           0                 0   
134946                    0           0                 0   
134948                    0           0                 0   
...                     ...         ...               ...   
2564854                   0           1                 0   
2564856                   0           1                 0   
2564857                   0           1                 0   
2564858                   0           1                 0   
2564860                   0           1                 0   

         time_span_int_arrival  weekend time_span time_span_int  \
134943                       0        0         0             0   
134944                       0

In [421]:
get_stats(during_week_nan_delay, ['tier_trips_count', 'tier_trips_end_at_station_count', 'nextbike_trips_count', 'nextbike_trips_end_at_station_count', 'current_temp', 'current_precipitation_volume'])

/tmp/ipykernel_2575952/41814695.py:51: RuntimeWarning: invalid value encountered in scalar divide
  qd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:55: RuntimeWarning: invalid value encountered in scalar divide
  cvqd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:51: RuntimeWarning: invalid value encountered in scalar divide
  qd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:55: RuntimeWarning: invalid value encountered in scalar divide
  cvqd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:51: RuntimeWarning: invalid value encountered in scalar divide
  qd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:55: RuntimeWarning: invalid value encountered in scalar divide
  cvqd = iqr / (percentile_75 + percentile_25)
/tmp/ipykernel_2575952/41814695.py:51: RuntimeWarning: invalid value encountered in scalar divide
  qd = iqr / (percentile_75 + percenti

column                                        tier_trips_count  \
rows                                                    623176   
sum                                                      11094   
mean                                                  0.017802   
median                                                     0.0   
mode               0    0
Name: tier_trips_count, dtype: int64   
max                                                          5   
min                                                          0   
std_dev                                               0.143835   
variance                                              0.020688   
skewness                                              9.352942   
kurtosis                                            110.415006   
percentile_25                                              0.0   
percentile_75                                              0.0   
iqr                                                        0.0   
range                                                        5   
cv                                                    8.079531   
qd                                                         NaN   
cs                                                   65.025648   
ck                                                  767.652253   
cvs                                                  65.025648   
cvk                                                 767.652253   
cvcs                                                 65.025648   
cvck                                                767.652253   
cvcv                                                  8.079531   
cvqd                                                       NaN   
cvr                                                 280.861727   
cvm                                                        1.0   
cvmed                                                      0.0   
cvmode         0    0.0
Name: tier_trips_count, dtype: float64   

column                           tier_trips_end_at_station_count  \
rows                                                      623176   
sum                                                         8986   
mean                                                     0.01442   
median                                                       0.0   
mode           0    0
Name: tier_trips_end_at_station_count, ...   
max                                                            4   
min                                                            0   
std_dev                                                  0.12869   
variance                                                0.016561   
skewness                                               10.227688   
kurtosis                                              129.379056   
percentile_25                                                0.0   
percentile_75                                                0.0   
iqr                                                          0.0   
range                                                          4   
cv                                                      8.924586   
qd                                                           NaN   
cs                                                     79.475581   
ck                                                    1005.35676   
cvs                                                    79.475581   
cvk                                                   1005.35676   
cvcs                                                   79.475581   
cvck                                                  1005.35676   
cvcv                                                    8.924586   
cvqd                                                         NaN   
cvr                                                    277.39862   
cvm                                                          1.0   
cvmed                                                        0.0   
cvmode         0    0.0
Name: tier_trips_end_at

In [422]:
during_week_nan_delay_tier = check_micromobility_datasets('tier', during_week_nan_delay)

KeyboardInterrupt: 

In [ ]:
during_week_nan_delay_tier.describe()

In [ ]:
get_stats(during_week_nan_delay_tier, ['trip_duration_seconds', 'trip_distance_kilometers'])

In [ ]:
# get entries where trips start and end at station
during_week_nan_delay_tier_station_station = during_week_nan_delay_tier[during_week_delay_tier['end_stop_id'].notna() & during_week_nan_delay_tier['start_stop_id'].notna()]
during_week_nan_delay_tier_station_station

In [ ]:
during_week_nan_delay_tier_station_station.describe()

In [ ]:
# get statistics for the tier trips that start and end at a station
get_stats(during_week_nan_delay_tier_station_station, ['trip_duration_seconds', 'trip_distance_kilometers'])

In [ ]:
during_week_nan_delay_next = check_micromobility_datasets('next', during_week_nan_delay)

In [ ]:
during_week_nan_delay_next.describe()

In [ ]:
get_stats(during_week_nan_delay_next, ['trip_duration_seconds', 'trip_distance_kilometers'])

In [ ]:
# get entries where trips start and end at station
during_week_nan_delay_next_station_station = during_week_nan_delay_next[during_week_nan_delay_next['end_stop_id'].notna() & during_week_nan_delay_next['start_stop_id'].notna()]
during_week_nan_delay_next_station_station

In [ ]:
during_week_nan_delay_next_station_station.describe()

In [ ]:
# get statistics for the tier trips that start and end at a station
get_stats(during_week_nan_delay_next_station_station, ['trip_duration_seconds', 'trip_distance_kilometers'])

In [ ]:
during_week_delay.describe()

In [ ]:
during_week_no_delay.describe()

In [ ]:
during_week_nan_delay.describe()

In [ ]:
friday_delay = delay[delay['weekday'].isin(['Friday'])]
friday_delay

In [ ]:
get_stats(friday_delay, ['tier_trips_count', 'tier_trips_end_at_station_count', 'nextbike_trips_count', 'nextbike_trips_end_at_station_count', 'current_temp', 'current_precipitation_volume'])

In [ ]:
friday_delay_tier = check_micromobility_datasets('tier', friday_delay)

In [ ]:
friday_delay_tier.describe()

In [ ]:
get_stats(friday_delay_tier, ['trip_duration_seconds', 'trip_distance_kilometers'])

In [ ]:
# get entries where trips start and end at station
friday_delay_tier_station_station = friday_delay_tier[friday_delay_tier['end_stop_id'].notna() & friday_delay_tier['start_stop_id'].notna()]
friday_delay_tier_station_station

In [ ]:
friday_delay_tier_station_station.describe()

In [ ]:
# get statistics for the tier trips that start and end at a station
get_stats(friday_delay_tier_station_station, ['trip_duration_seconds', 'trip_distance_kilometers'])

In [ ]:
friday_delay_next = check_micromobility_datasets('next', friday_delay)

In [ ]:
friday_delay_next.describe()

In [ ]:
get_stats(friday_delay_next, ['trip_duration_seconds', 'trip_distance_kilometers'])

In [ ]:
# get entries where trips start and end at station
friday_delay_next_station_station = friday_delay_next[friday_delay_next['end_stop_id'].notna() & friday_delay_next['start_stop_id'].notna()]
friday_delay_next_station_station

In [ ]:
friday_delay_next_station_station.describe()

In [ ]:
# get statistics for the tier trips that start and end at a station
get_stats(friday_delay_next_station_station, ['trip_duration_seconds', 'trip_distance_kilometers'])

In [ ]:
friday_no_delay = no_delay[no_delay['weekday'].isin(['Friday'])]
friday_no_delay

In [ ]:
get_stats(friday_no_delay, ['tier_trips_count', 'tier_trips_end_at_station_count', 'nextbike_trips_count', 'nextbike_trips_end_at_station_count', 'current_temp', 'current_precipitation_volume'])

In [ ]:
friday_no_delay_tier = check_micromobility_datasets('tier', friday_no_delay)

In [ ]:
friday_no_delay_tier.describe()

In [ ]:
get_stats(friday_no_delay_tier, ['trip_duration_seconds', 'trip_distance_kilometers'])

In [ ]:
# get entries where trips start and end at station
friday_no_delay_tier_station_station = friday_no_delay_tier[friday_no_delay_tier['end_stop_id'].notna() & friday_no_delay_tier['start_stop_id'].notna()]
friday_no_delay_tier_station_station

In [ ]:
friday_no_delay_tier_station_station.describe()

In [ ]:
# get statistics for the tier trips that start and end at a station
get_stats(friday_no_delay_tier_station_station, ['trip_duration_seconds', 'trip_distance_kilometers'])

In [ ]:
friday_no_delay_next = check_micromobility_datasets('next', friday_no_delay)

In [ ]:
friday_no_delay_next.describe()

In [ ]:
get_stats(friday_no_delay_next, ['trip_duration_seconds', 'trip_distance_kilometers'])

In [ ]:
# get entries where trips start and end at station
friday_no_delay_next_station_station = friday_no_delay_next[friday_no_delay_next['end_stop_id'].notna() & friday_no_delay_next['start_stop_id'].notna()]
friday_no_delay_next_station_station

In [ ]:
friday_no_delay_next_station_station.describe()

In [ ]:
# get statistics for the tier trips that start and end at a station
get_stats(friday_no_delay_next_station_station, ['trip_duration_seconds', 'trip_distance_kilometers'])

In [ ]:
friday_nan_delay = nan_delay[nan_delay['weekday'].isin(['Friday'])]
friday_nan_delay

In [ ]:
get_stats(friday_nan_delay, ['tier_trips_count', 'tier_trips_end_at_station_count', 'nextbike_trips_count', 'nextbike_trips_end_at_station_count', 'current_temp', 'current_precipitation_volume'])

In [ ]:
friday_nan_delay_tier = check_micromobility_datasets('tier', friday_nan_delay)

In [ ]:
friday_nan_delay_tier.describe()

In [ ]:
get_stats(friday_nan_delay_tier, ['trip_duration_seconds', 'trip_distance_kilometers'])

In [ ]:
# get entries where trips start and end at station
friday_nan_delay_tier_station_station = friday_nan_delay_tier[friday_nan_delay_tier['end_stop_id'].notna() & friday_nan_delay_tier['start_stop_id'].notna()]
friday_nan_delay_tier_station_station

In [ ]:
friday_nan_delay_tier_station_station.describe()

In [ ]:
# get statistics for the tier trips that start and end at a station
get_stats(friday_nan_delay_tier_station_station, ['trip_duration_seconds', 'trip_distance_kilometers'])

In [ ]:
friday_nan_delay_next = check_micromobility_datasets('next', friday_nan_delay)

In [ ]:
friday_nan_delay_next.describe()

In [ ]:
get_stats(friday_nan_delay_next, ['trip_duration_seconds', 'trip_distance_kilometers'])

In [ ]:
# get entries where trips start and end at station
friday_nan_delay_next_station_station = friday_nan_delay_next[friday_nan_delay_next['end_stop_id'].notna() & friday_nan_delay_next['start_stop_id'].notna()]
friday_nan_delay_next_station_station

In [ ]:
friday_nan_delay_next_station_station.describe()

In [ ]:
# get statistics for the tier trips that start and end at a station
get_stats(friday_nan_delay_next_station_station, ['trip_duration_seconds', 'trip_distance_kilometers'])

In [ ]:
friday_delay.describe()

In [ ]:
friday_no_delay.describe()

In [ ]:
friday_nan_delay.describe()

In [ ]:
saturday_delay = delay[delay['weekday'].isin(['Saturday'])]
saturday_delay

In [ ]:
get_stats(saturday_delay, ['tier_trips_count', 'tier_trips_end_at_station_count', 'nextbike_trips_count', 'nextbike_trips_end_at_station_count', 'current_temp', 'current_precipitation_volume'])

In [ ]:
saturday_delay_tier = check_micromobility_datasets('tier', saturday_delay)

In [ ]:
saturday_delay_tier.describe()

In [ ]:
get_stats(saturday_delay_tier, ['trip_duration_seconds', 'trip_distance_kilometers'])

In [ ]:
# get entries where trips start and end at station
saturday_delay_tier_station_station = saturday_delay_tier[saturday_delay_tier['end_stop_id'].notna() & saturday_delay_tier['start_stop_id'].notna()]
saturday_delay_tier_station_station

In [ ]:
saturday_delay_tier_station_station.describe()

In [ ]:
# get statistics for the tier trips that start and end at a station
get_stats(saturday_delay_tier_station_station, ['trip_duration_seconds', 'trip_distance_kilometers'])

In [ ]:
saturday_delay_next = check_micromobility_datasets('next', saturday_delay)

In [ ]:
saturday_delay_next.describe()

In [ ]:
get_stats(saturday_delay_next, ['trip_duration_seconds', 'trip_distance_kilometers'])

In [ ]:
# get entries where trips start and end at station
saturday_delay_next_station_station = saturday_delay_next[saturday_delay_next['end_stop_id'].notna() & saturday_delay_next['start_stop_id'].notna()]
saturday_delay_next_station_station

In [ ]:
saturday_delay_next_station_station.describe()

In [ ]:
# get statistics for the tier trips that start and end at a station
get_stats(saturday_delay_next_station_station, ['trip_duration_seconds', 'trip_distance_kilometers'])

In [ ]:
saturday_no_delay = no_delay[no_delay['weekday'].isin(['Saturday'])]
saturday_no_delay

In [ ]:
get_stats(saturday_no_delay, ['tier_trips_count', 'tier_trips_end_at_station_count', 'nextbike_trips_count', 'nextbike_trips_end_at_station_count', 'current_temp', 'current_precipitation_volume'])

In [ ]:
saturday_no_delay_tier = check_micromobility_datasets('tier', saturday_no_delay)

In [ ]:
saturday_no_delay_tier.describe()

In [ ]:
get_stats(saturday_no_delay_tier, ['trip_duration_seconds', 'trip_distance_kilometers'])

In [ ]:
# get entries where trips start and end at station
saturday_no_delay_tier_station_station = saturday_no_delay_tier[saturday_no_delay_tier['end_stop_id'].notna() & saturday_no_delay_tier['start_stop_id'].notna()]
saturday_no_delay_tier_station_station

In [ ]:
saturday_no_delay_tier_station_station.describe()

In [ ]:
# get statistics for the tier trips that start and end at a station
get_stats(saturday_no_delay_tier_station_station, ['trip_duration_seconds', 'trip_distance_kilometers'])

In [ ]:
saturday_no_delay_next = check_micromobility_datasets('next', saturday_no_delay)

In [ ]:
saturday_no_delay_next.describe()

In [ ]:
get_stats(saturday_no_delay_next, ['trip_duration_seconds', 'trip_distance_kilometers'])

In [ ]:
# get entries where trips start and end at station
saturday_no_delay_next_station_station = saturday_no_delay_next[saturday_no_delay_next['end_stop_id'].notna() & saturday_no_delay_next['start_stop_id'].notna()]
saturday_no_delay_next_station_station

In [ ]:
saturday_no_delay_next_station_station.describe()

In [ ]:
# get statistics for the tier trips that start and end at a station
get_stats(saturday_no_delay_next_station_station, ['trip_duration_seconds', 'trip_distance_kilometers'])

In [ ]:
saturday_nan_delay = nan_delay[nan_delay['weekday'].isin(['Saturday'])]
saturday_nan_delay

In [ ]:
get_stats(saturday_nan_delay, ['tier_trips_count', 'tier_trips_end_at_station_count', 'nextbike_trips_count', 'nextbike_trips_end_at_station_count', 'current_temp', 'current_precipitation_volume'])

In [ ]:
saturday_nan_delay_tier = check_micromobility_datasets('tier', saturday_nan_delay)

In [ ]:
saturday_nan_delay_tier.describe()

In [ ]:
get_stats(saturday_nan_delay_tier, ['trip_duration_seconds', 'trip_distance_kilometers'])

In [ ]:
# get entries where trips start and end at station
saturday_nan_delay_tier_station_station = saturday_nan_delay_tier[saturday_nan_delay_tier['end_stop_id'].notna() & saturday_nan_delay_tier['start_stop_id'].notna()]
saturday_nan_delay_tier_station_station

In [ ]:
saturday_nan_delay_tier_station_station.describe()

In [ ]:
# get statistics for the tier trips that start and end at a station
get_stats(saturday_nan_delay_tier_station_station, ['trip_duration_seconds', 'trip_distance_kilometers'])

In [ ]:
saturday_nan_delay_next = check_micromobility_datasets('next', saturday_nan_delay)

In [ ]:
saturday_nan_delay_next.describe()

In [ ]:
get_stats(saturday_nan_delay_next, ['trip_duration_seconds', 'trip_distance_kilometers'])

In [ ]:
# get entries where trips start and end at station
saturday_nan_delay_next_station_station = saturday_nan_delay_next[saturday_nan_delay_next['end_stop_id'].notna() & saturday_nan_delay_next['start_stop_id'].notna()]
saturday_nan_delay_next_station_station

In [ ]:
saturday_nan_delay_next_station_station.describe()

In [ ]:
# get statistics for the tier trips that start and end at a station
get_stats(saturday_nan_delay_next_station_station, ['trip_duration_seconds', 'trip_distance_kilometers'])

In [ ]:
saturday_delay.describe()

In [ ]:
saturday_no_delay.describe()

In [ ]:
saturday_nan_delay.describe()

In [ ]:
sunday_delay = delay[delay['weekday'].isin(['Sunday'])]
sunday_delay

In [ ]:
get_stats(sunday_delay, ['tier_trips_count', 'tier_trips_end_at_station_count', 'nextbike_trips_count', 'nextbike_trips_end_at_station_count', 'current_temp', 'current_precipitation_volume'])

In [ ]:
sunday_delay_tier = check_micromobility_datasets('tier', sunday_delay)

In [ ]:
sunday_delay_tier.describe()

In [ ]:
get_stats(sunday_delay_tier, ['trip_duration_seconds', 'trip_distance_kilometers'])

In [ ]:
# get entries where trips start and end at station
sunday_delay_tier_station_station = sunday_delay_tier[sunday_delay_tier['end_stop_id'].notna() & sunday_delay_tier['start_stop_id'].notna()]
sunday_delay_tier_station_station

In [ ]:
sunday_delay_tier_station_station.describe()

In [ ]:
# get statistics for the tier trips that start and end at a station
get_stats(sunday_delay_tier_station_station, ['trip_duration_seconds', 'trip_distance_kilometers'])

In [ ]:
sunday_delay_next = check_micromobility_datasets('next', sunday_delay)

In [ ]:
sunday_delay_next.describe()

In [ ]:
get_stats(sunday_delay_next, ['trip_duration_seconds', 'trip_distance_kilometers'])

In [ ]:
# get entries where trips start and end at station
sunday_delay_next_station_station = sunday_delay_next[sunday_delay_next['end_stop_id'].notna() & sunday_delay_next['start_stop_id'].notna()]
sunday_delay_next_station_station

In [ ]:
sunday_delay_next_station_station.describe()

In [ ]:
# get statistics for the tier trips that start and end at a station
get_stats(sunday_delay_next_station_station, ['trip_duration_seconds', 'trip_distance_kilometers'])

In [ ]:
sunday_no_delay = no_delay[no_delay['weekday'].isin(['Sunday'])]
sunday_no_delay

In [ ]:
get_stats(sunday_no_delay, ['tier_trips_count', 'tier_trips_end_at_station_count', 'nextbike_trips_count', 'nextbike_trips_end_at_station_count', 'current_temp', 'current_precipitation_volume'])

In [ ]:
sunday_no_delay_tier = check_micromobility_datasets('tier', sunday_no_delay)

In [ ]:
sunday_no_delay_tier.describe()

In [ ]:
get_stats(sunday_no_delay_tier, ['trip_duration_seconds', 'trip_distance_kilometers'])

In [ ]:
# get entries where trips start and end at station
sunday_no_delay_tier_station_station = sunday_no_delay_tier[sunday_no_delay_tier['end_stop_id'].notna() & sunday_no_delay_tier['start_stop_id'].notna()]
sunday_no_delay_tier_station_station

In [ ]:
sunday_no_delay_tier_station_station.describe()

In [ ]:
# get statistics for the tier trips that start and end at a station
get_stats(sunday_no_delay_tier_station_station, ['trip_duration_seconds', 'trip_distance_kilometers'])

In [ ]:
sunday_no_delay_next = check_micromobility_datasets('next', sunday_no_delay)

In [ ]:
sunday_no_delay_next.describe()

In [ ]:
get_stats(sunday_no_delay_next, ['trip_duration_seconds', 'trip_distance_kilometers'])

In [ ]:
# get entries where trips start and end at station
sunday_no_delay_next_station_station = sunday_no_delay_next[sunday_no_delay_next['end_stop_id'].notna() & sunday_no_delay_next['start_stop_id'].notna()]
sunday_no_delay_next_station_station

In [ ]:
sunday_no_delay_next_station_station.describe()

In [ ]:
# get statistics for the tier trips that start and end at a station
get_stats(sunday_no_delay_next_station_station, ['trip_duration_seconds', 'trip_distance_kilometers'])

In [ ]:
sunday_nan_delay = nan_delay[nan_delay['weekday'].isin(['Sunday'])]
sunday_nan_delay

In [ ]:
get_stats(sunday_nan_delay, ['tier_trips_count', 'tier_trips_end_at_station_count', 'nextbike_trips_count', 'nextbike_trips_end_at_station_count', 'current_temp', 'current_precipitation_volume'])

In [ ]:
sunday_nan_delay_tier = check_micromobility_datasets('tier', sunday_nan_delay)

In [ ]:
sunday_nan_delay_tier.describe()

In [ ]:
get_stats(sunday_nan_delay_tier, ['trip_duration_seconds', 'trip_distance_kilometers'])

In [ ]:
# get entries where trips start and end at station
sunday_nan_delay_tier_station_station = sunday_nan_delay_tier[sunday_nan_delay_tier['end_stop_id'].notna() & sunday_nan_delay_tier['start_stop_id'].notna()]
sunday_nan_delay_tier_station_station

In [ ]:
sunday_nan_delay_tier_station_station.describe()

In [ ]:
# get statistics for the tier trips that start and end at a station
get_stats(sunday_nan_delay_tier_station_station, ['trip_duration_seconds', 'trip_distance_kilometers'])

In [ ]:
sunday_nan_delay_next = check_micromobility_datasets('next', sunday_nan_delay)

In [ ]:
sunday_nan_delay_next.describe()

In [ ]:
get_stats(sunday_nan_delay_next, ['trip_duration_seconds', 'trip_distance_kilometers'])

In [ ]:
# get entries where trips start and end at station
sunday_nan_delay_next_station_station = sunday_nan_delay_next[sunday_nan_delay_next['end_stop_id'].notna() & sunday_nan_delay_next['start_stop_id'].notna()]
sunday_nan_delay_next_station_station

In [ ]:
sunday_nan_delay_next_station_station.describe()

In [ ]:
# get statistics for the tier trips that start and end at a station
get_stats(sunday_nan_delay_next_station_station, ['trip_duration_seconds', 'trip_distance_kilometers'])

In [ ]:
sunday_delay.describe()

In [ ]:
sunday_no_delay.describe()

In [ ]:
sunday_nan_delay.describe()